In [31]:
# Generic imports
import pandas as pd
from typing import Tuple, cast
import plotly.express as px
import warnings

warnings.filterwarnings("ignore")

In [32]:
# Local imports - see https://github.com/jakee417/bayesian-opt/tree/master
from thompson_sampling import PathwiseThompsonSampling
from plotting_helpers import *

In [33]:
# Ax & BoTorch imports
from ax.service.ax_client import AxClient, ObjectiveProperties
from ax.modelbridge.generation_strategy import GenerationStep, GenerationStrategy
from ax.models.torch.botorch_modular.surrogate import Surrogate
from ax.modelbridge.registry import Models
from ax.utils.common.typeutils import not_none
from ax.core.types import TParameterization, TEvaluationOutcome, TModelPredict
from ax.core.observation import ObservationFeatures
from ax.modelbridge import TorchModelBridge
from ax.plot.diagnostic import interact_cross_validation_plotly
from ax.plot.contour import interact_contour_plotly
from ax.utils.notebook.plotting import render
from ax.modelbridge.cross_validation import cross_validate, compute_diagnostics
from botorch.acquisition.analytic import (
    ProbabilityOfImprovement,
    ExpectedImprovement,
    UpperConfidenceBound,
)
from botorch.models.gp_regression import SingleTaskGP

## Mining Gold!
I used [this website](https://frnsys.com/misc/polynomial_designer/) to recreate the gold content function from the OP.

In [34]:
def gold(x: float) -> float:
    return (
        2.85
        + 9.20 * np.power(x, 1)
        + -8.32e0 * np.power(x, 2)
        + 2.39 * np.power(x, 3)
        + -2.10e-1 * np.power(x, 4)
    )

In [35]:
# Gold can occur between 0 and 6.
x = np.linspace(0, 6)
# Setup our observation features to use for model predictions.
observation_features = [
    ObservationFeatures(
        parameters={"x": i},
    )
    for i in x
]
y = [gold(i) for i in x]

Plot the gold content function over our domain.

In [36]:
render_plotly_html(
    px.line(
        pd.DataFrame({"X": x, "Gold Content": y}),
        x="X",
        y="Gold Content",
        title="Ground Truth for Gold Content",
    )
)

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="8a638fb3-4342-424a-b98b-3b9f8fb7d371" class="plotly-graph-div" style="height:100%; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("8a638fb3-4342-424a-b98b-3b9f8fb7d371")) {                    Plotly.newPlot(                        "8a638fb3-4342-424a-b98b-3b9f8fb7d371",                        [{"hovertemplate":"X=%{x}\u003cbr\u003eGold Content=%{y}\u003cextra\u003e\u003c\u002fextra\u003e","legendgroup":"","line":{"color":"#636efa","dash":"solid"},"marker":{"symbol":"circle"},"mode":"lines","name":"","orientation":"v","showlegend":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"xaxis":"x","y":[2.85,3.856123347536194,4.638417508253971,5.221510704359092,5.628898102467025,5.8829418136029314,6.00487089320169,6.01478134110787,5.9316361015757515,5.773265063269314,5.5563650592622364,5.296499867037907,5.008100208489416,4.7044637499195545,4.397755102040818,4.099005819975396,3.818114403255205,3.5638462958218278,3.343833886026604,3.1645765066304996,3.0314404348042556,2.948658892128277,2.919332044592691,2.9454270025973184,3.0277778209516644,3.166085498874992,3.3589179799961926,3.6037101523539157,3.896763848396514,4.233247844982003,4.607197863378097,5.011516569262348,5.4379735727217735,5.877205428253326,6.318715634763429,6.7508746355685645,7.1609198183944756,7.534955515376893,7.857953003061169,8.113750502402425,8.28505317876541,8.35343314192454,8.29932944606415,8.10204808977798,7.739762016069648,7.18951111235242,6.427202210449309,5.42760908659298,4.164372461425842,2.6100000000000705],"yaxis":"y","type":"scatter"}],                        {"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}},"xaxis":{"anchor":"y","domain":[0.0,1.0],"title":{"text":"X"}},"yaxis":{"anchor":"x","domain":[0.0,1.0],"title":{"text":"Gold Content"}},"legend":{"tracegroupgap":0},"title":{"text":"Ground Truth for Gold Content"}},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>

## Active Learning

### Ax Helper Functions
First, define some helper functions for common Ax operations.

In [37]:
def evaluate(parameterization: TParameterization) -> TEvaluationOutcome:
    """Evaluate a parameterization on our groundtruth gold function."""
    x = cast(float, parameterization.get("x", 0.0))
    y = gold(x)
    return {"gold": (y, None)}


def create_generation_strategy(
    botorch_acqf_class, random_class=Models.SOBOL, random_trials: int = 3
) -> GenerationStrategy:
    """Strategy consisting of random search followed by surrogate/acquisition."""
    return GenerationStrategy(
        steps=[
            # Always include random steps.
            GenerationStep(
                model=random_class,
                num_trials=random_trials,
            ),
            # Combine an acquisition class with a GP surrogate function.
            GenerationStep(
                model=Models.BOTORCH_MODULAR,
                num_trials=-1,
                model_kwargs={
                    "botorch_acqf_class": botorch_acqf_class,
                    "surrogate": Surrogate(SingleTaskGP),
                },
            ),
        ]
    )


def create_client(generation_strategy: GenerationStrategy) -> AxClient:
    """Create a ax client for the gold content experiment."""
    ax_client = AxClient(
        generation_strategy=generation_strategy,
        random_seed=1,
        verbose_logging=False,
    )
    ax_client.create_experiment(
        name="gold_content",
        parameters=[
            {
                "name": "x",
                "type": "range",
                "bounds": [0.0, 6.0],
                "value_type": "float",
                "log_scale": False,
            },
        ],
        # We want to get the most gold possible.
        objectives={"gold": ObjectiveProperties(minimize=False)},
    )
    return ax_client


Cache = Tuple[Dict[int, TModelPredict], Dict[int, List[List[float]]]]


def run_ax(n: int, ax_client: AxClient, acqf_n: int = 1) -> Cache:
    """Run an ax client for a specified number of iterations."""
    predictions: Dict[int, TModelPredict] = {}
    acquisitions: Dict[int, List[List[float]]] = {}
    for i in range(n):
        # Get the next trial's parameterization.
        parameterization, trial_index = ax_client.get_next_trial()
        # Extract the model for caching this iteration.
        model = cast(
            TorchModelBridge,
            not_none(ax_client.generation_strategy.model),
        )
        # We won't always have an TorchModelBridge that supports evaluation.
        # If we do, run evaluation and cache the results for visualizing.
        try:
            predictions[i] = model.predict(
                observation_features=observation_features,
            )
            acquisitions[i] = [
                model.evaluate_acquisition_function(
                    observation_features=observation_features
                )
                for _ in range(acqf_n)
            ]
        except Exception:
            pass
        # Complete the trial by evaluating the true gold content.
        ax_client.complete_trial(
            trial_index=trial_index, raw_data=evaluate(parameterization)
        )
    return predictions, acquisitions

Store results of each optimization so we can compare the different methods at the end of this section.

In [38]:
results: Dict[str, pd.DataFrame] = {}

### Surrogate Function

Sample uniformly from the domain to show how we learn the gold content with our surrogate function. Our surrogate function will be a [Gaussian Process](https://cs229.stanford.edu/section/cs229-gaussian_processes.pdf):

$$
\begin{align*}
  \begin{bmatrix}
    f(x_1) \\
    \vdots \\
    f(x_m)
  \end{bmatrix}
  &\sim \mathcal N \big(\begin{bmatrix}
    m(x_1) \\
    \vdots \\
    m(x_m)
  \end{bmatrix}, 
  \begin{bmatrix}
    k(x_1, x_1) & \dots & k(x_1, x_m) \\
    \vdots & \ddots & \vdots \\
    k(x_m, x_1) & \dots & k(x_m, x_m)
  \end{bmatrix} \big) \\
m(x) &= \mathbb E[x] \\
k(x, x') &= \mathbb E[(x - m(x))(x' - m(x'))] \\
y^{(i)} &= f(x^{(i)}) + \epsilon^{(i)},\quad i=1,\dots,m, \quad \epsilon^{(i)}\sim N(0, \sigma^2)
\end{align*}
$$

In [39]:
generation_strategy = create_generation_strategy(
    botorch_acqf_class=ProbabilityOfImprovement,
    random_class=Models.UNIFORM,
    random_trials=5,
)
ax_client = create_client(generation_strategy=generation_strategy)
predictions, acquisitions = run_ax(n=10, ax_client=ax_client)

[WARNING 08-11 10:42:37] ax.service.ax_client: Random seed set to 1. Note that this setting only affects the Sobol quasi-random generator and BoTorch-powered Bayesian optimization models. For the latter models, setting random seed to the same number for two optimizations will make the generated trials similar, but not exactly the same, and over time the trials will diverge more.
[INFO 08-11 10:42:37] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[RangeParameter(name='x', parameter_type=FLOAT, range=[0.0, 6.0])], parameter_constraints=[]).


Plotly can be animated by adding a [slider](https://plotly.com/python/sliders/) to the figure layout. Note, the first couple points are the uniformly random samples. These are followed by alternating the surrogate function and a query point.

In [40]:
fig = go.Figure()
# Plot our groundtruth function for comparison.
fig.add_trace(plot_groundtruth(x=x, y=y, kwargs=get_line_kwargs()))
# Iterate through the trials.
n = len(ax_client.generation_strategy._generator_runs)
j = len(fig.data)
for i in range(n):
    # Not every iteration has predictions.
    if i in predictions:
        fig.add_trace(
            plot_predictions(x=x, predictions=predictions, i=i),
        )
    # Finally, add where we observed this iteration.
    fig.add_trace(
        plot_observed(
            ax_client=ax_client,
            gold_fn=gold,
            i=i,
            kwargs=get_scatter_kwargs(),
        )
    )
# Create the animation steps.
steps = [
    dict(
        method="update",
        label=fig.data[i].name,
        args=[
            {
                "visible": [True] * (j + i) + [False] * (len(fig.data)),
                "title": str(i),
            }
        ],
    )
    for i in range(len(fig.data))
]
# Format the layout of the plot
fig.update_yaxes(range=[1, 9])
fig.update_xaxes(range=[-1, 7])
fig.update_layout(
    title="Gold Search",
    xaxis=dict(title="X"),
    yaxis=dict(title="Gold Content"),
    # Add the animation steps onto the layout.
    sliders=[dict(active=0, steps=steps)],
)
render_plotly_html(fig)

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="47fecd72-ba00-4576-a81d-084ff28356f0" class="plotly-graph-div" style="height:100%; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("47fecd72-ba00-4576-a81d-084ff28356f0")) {                    Plotly.newPlot(                        "47fecd72-ba00-4576-a81d-084ff28356f0",                        [{"hoverinfo":"skip","mode":"lines","name":"Ground Truth (f)","showlegend":true,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[2.85,3.856123347536194,4.638417508253971,5.221510704359092,5.628898102467025,5.8829418136029314,6.00487089320169,6.01478134110787,5.9316361015757515,5.773265063269314,5.5563650592622364,5.296499867037907,5.008100208489416,4.7044637499195545,4.397755102040818,4.099005819975396,3.818114403255205,3.5638462958218278,3.343833886026604,3.1645765066304996,3.0314404348042556,2.948658892128277,2.919332044592691,2.9454270025973184,3.0277778209516644,3.166085498874992,3.3589179799961926,3.6037101523539157,3.896763848396514,4.233247844982003,4.607197863378097,5.011516569262348,5.4379735727217735,5.877205428253326,6.318715634763429,6.7508746355685645,7.1609198183944756,7.534955515376893,7.857953003061169,8.113750502402425,8.28505317876541,8.35343314192454,8.29932944606415,8.10204808977798,7.739762016069648,7.18951111235242,6.427202210449309,5.42760908659298,4.164372461425842,2.6100000000000705],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=1","opacity":1.0,"showlegend":true,"visible":false,"x":[0.32872711926390363],"y":[5.057664805217066],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=2","opacity":1.0,"showlegend":true,"visible":false,"x":[1.4348541948065263],"y":[5.091532753266253],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=3","opacity":1.0,"showlegend":true,"visible":false,"x":[1.1448646473418669],"y":[5.703244208949001],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=4","opacity":1.0,"showlegend":true,"visible":false,"x":[4.012995102221842],"y":[5.776814007863983],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=5","opacity":1.0,"showlegend":true,"visible":false,"x":[2.451072738768894],"y":[3.0295919107202014],"type":"scatter"},{"fill":"toself","hoverinfo":"skip","name":"p=6","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[5.07316634384684,4.999504522910488,5.032634654794059,5.164273638531742,5.3575527850944376,5.5568489891338,5.711965298159969,5.793407593601372,5.793046710584509,5.714025272511392,5.5600243071368824,5.337923204662083,5.070524245665279,4.788961815910491,4.509782877049986,4.231677995788834,3.9480319023640744,3.6620736253279857,3.39643006646367,3.192706536745609,3.099594778508046,3.1508663930297627,3.3459010613785805,3.6534271369530398,4.026144048242655,4.413922289654745,4.773380320739256,5.073826644284898,5.300281527146908,5.454264163752668,5.552622538439179,5.624192584556933,5.703762590807438,5.822971404330607,5.99911603888284,6.229694457181241,6.498491485685141,6.783974911678316,7.065474533162904,7.326647652755239,7.55671286607771,7.750218586592451,7.906049409724522,8.02618143070912,8.114497290043163,8.175813139212142,8.215163557391369,8.23732952209914,8.246566238545071,8.246479913608551,2.1038117576686997,2.199054270314816,2.3146515175484197,2.454304178794718,2.6219121269328403,2.821286080558268,3.0556775521343984,3.3270771103308348,3.6352434209155113,3.9764615523321556,4.342102095479228,4.717177358659123,5.079277254857443,5.398508766827107,5.639314402783944,5.765194097747739,5.747192701884677,5.576172607972804,5.273003013151644,4.881693970881187,4.454369317829374,4.039878164752305,3.6767265690557367,3.3894657457024477,3.1876287569198007,3.0666662403321716,3.010814888092022,2.998176501454861,3.0081848661092496,3.030702344003669,3.073740034884545,3.162093953009095,3.322827933956939,3.569615051916137,3.894282847692029,4.267682326786479,4.649030655275435,4.999768614540697,5.294025964716555,5.515119030153113,5.643537656434499,5.6682908988889835,5.606217448075431,5.493531441859911,5.36459781712188,5.234645610425719,5.094845010060559,4.922132176436568,4.698442022644098,4.421796493248411],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=6","opacity":1.0,"showlegend":true,"visible":false,"x":[4.194693878482701],"y":[6.431018758151026],"type":"scatter"},{"fill":"toself","hoverinfo":"skip","name":"p=7","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[5.011682324084294,4.967292420626053,5.025202045358007,5.167691506803046,5.35759903216066,5.547168449602896,5.694598673597294,5.773959136627116,5.775509317842225,5.699511018224228,5.550181987100491,5.3373942847125,5.082027050882892,4.808793912710115,4.531893404446643,4.253455542677204,3.971746765137313,3.6912837140884633,3.4293691920870373,3.2157764648311256,3.0846628857866976,3.060292735828231,3.1446283048135526,3.3187977990490745,3.5524082396772885,3.8134444764344906,4.076296630963971,4.326743674647874,4.563468597947743,4.796146785075203,5.0405339217118525,5.311499066013494,5.615756306118919,5.947097660441558,6.2881466518593205,6.624132963507047,6.954400881726091,7.285305283663272,7.6214249824415825,7.962303750557356,8.302792271205293,8.634917506364527,8.949959232100325,9.24008618238094,9.499354068036084,9.724112888748968,9.91297272384869,10.066494452268351,10.186747760928867,10.276840394120928,2.4965911970642187,2.813154012031427,3.16428410971422,3.5483202271228196,3.961176468593514,4.395693472714459,4.841050846766807,5.282377259414732,5.700747757610311,6.073802111417138,6.377227999976317,6.587287765666102,6.6843713658020985,6.657173596066782,6.506507431817513,6.2471257817942165,5.905170436837344,5.506829751551806,5.071205977287646,4.617833080232228,4.171542923542104,3.7606068620992783,3.4116167660073353,3.1440573572851385,2.966415397344681,2.874810571196833,2.8545611925303187,2.8846572335391953,2.944583349133419,3.022110487173903,3.119394142106782,3.2520810268354223,3.438733673862437,3.6890795552786795,3.9973051345597783,4.342174713201126,4.6932464960203255,5.020030222256385,5.29868887712577,5.510632776542448,5.63786040625332,5.671791673736523,5.624734746493644,5.523755297786458,5.396327195188752,5.257711648848211,5.105803731317368,4.925695757685748,4.701521788073669,4.4257313336465565],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=7","opacity":1.0,"showlegend":true,"visible":false,"x":[4.491198145517794],"y":[7.41938481136026],"type":"scatter"},{"fill":"toself","hoverinfo":"skip","name":"p=8","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[4.688935158788733,4.757263160615211,4.9151940262942935,5.134072034212077,5.374241300214174,5.593106914798788,5.756281377409039,5.842577941386738,5.842147001903871,5.751541476554139,5.5718213954975475,5.314564636658083,5.00737239981946,4.684544268081935,4.370780256336546,4.076644725009364,3.8035766609236195,3.5522523872648795,3.3294254705432156,3.149906502890123,3.032564015291765,2.9916573240373903,3.028825376678319,3.1330456504453497,3.2862045300608713,3.469976102799417,3.6716546641515455,3.887435044406619,4.122454519809857,4.3877050809853815,4.694703266390146,5.049558869425854,5.448686085515852,5.878452710084925,6.319765515819786,6.754196286926548,7.163335220172872,7.532886751931623,7.862797880872357,8.1661554444958,8.461075522557168,8.764060951480399,9.086359390352856,9.432854925393542,9.802622312785426,10.190333919155057,10.587923474378039,10.986136097637678,11.375776231328494,11.748591955594595,4.59768284060668,5.209894091630055,5.810774805544268,6.382891156057303,6.906816783258837,7.3621427802900765,7.728961711771088,7.9898044823152725,8.13189367060431,8.149409387174314,8.045256675324776,7.831632288981851,7.528656221367233,7.160756628149617,6.751172605735728,6.317848788216408,5.876645512312088,5.439517660355619,5.010475483930592,4.591987112990491,4.1915487085287735,3.8229928033293814,3.5034571857165453,3.2483785741252547,3.0668035070187454,2.9586888161259077,2.9150933476311685,2.9213679765697833,2.9626394166254744,3.030046001970331,3.125336023268469,3.259945114954613,3.4468845744693204,3.691967901689031,3.9892409555014274,4.321889365645164,4.667455647787947,5.003948810056101,5.311901565631748,5.569224984381501,5.747870468067624,5.825894449897707,5.802356667900556,5.695999817585351,5.534406224061591,5.341540169415405,5.129189423455499,4.895517371157193,4.630674455417304,4.324414590323383],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=8","opacity":1.0,"showlegend":true,"visible":false,"x":[4.608163665936905],"y":[7.746444938096204],"type":"scatter"},{"fill":"toself","hoverinfo":"skip","name":"p=9","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[4.575519201693577,4.699806649386003,4.896328546588739,5.136835688306437,5.385773660386025,5.606425046981714,5.7689602366772075,5.853946860038738,5.851156268240532,5.756645032505787,5.572493884077128,5.311997802970214,5.002473230806389,4.67617354546572,4.357154443142613,4.057822317331819,3.782586648183381,3.534040272174998,3.3181571808604344,3.1460216601573534,3.0312398995763146,2.9840215257076594,3.0056842698339796,3.0885854992390094,3.220056788124329,3.387377482180945,3.5819741546033828,3.8016384897876683,4.050228121852698,4.335009305574577,4.662472288201293,5.034037006739993,5.443415333198203,5.8771659540134555,6.318600859707222,6.75196570878708,7.161756942537717,7.534305503211123,7.860976562683477,8.141838219282375,8.387129935215114,8.613459387302207,8.838916274194304,9.0792567892431,9.345706313713913,9.644210060570536,9.975718374923915,10.337079607800096,10.722193280060106,11.12317993510144,5.935293020410067,6.520710120715554,7.0549996632607055,7.522193708343121,7.907475932189097,8.198497713938556,8.386758622939968,8.468832242469528,8.447120651453567,8.329748501336947,8.129230459099285,7.859799820448051,7.53401952143703,7.161142056785434,6.751374173881461,6.318215875875912,5.876822186256043,5.4405752735292,5.016216468019225,4.6074962895502765,4.220576348127558,3.865906800226299,3.5566186817383874,3.3050120575533417,3.1189398254305107,2.9995282631109097,2.9410792640093435,2.933318250987459,2.965448535463811,3.0307917913356035,3.130186480406596,3.2713252402945034,3.462844067733325,3.7078649057968507,4.000554035137165,4.3266393852185585,4.666983811522136,5.001656137906867,5.31093830175758,5.571525297354402,5.75568147790567,5.842191433453518,5.828216916822813,5.728212769978933,5.565623985989545,5.363000540930447,5.134494173767781,4.883303413258469,4.604525192950797,4.290545060042975],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=9","opacity":1.0,"showlegend":true,"visible":false,"x":[4.699603014745402],"y":[7.964008751168905],"type":"scatter"},{"fill":"toself","hoverinfo":"skip","name":"p=10","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[4.554023286522054,4.6894248140034165,4.893371282488958,5.137844228155514,5.3881694273653435,5.608794782911614,5.770798868873624,5.85516432778863,5.851724952661134,5.756591964706958,5.572116195742437,5.311838811326354,5.002819296471501,4.676700681543766,4.357240361677949,4.057089882233097,3.7812081005024885,3.5326311538921042,3.317345668051653,3.145945154634501,3.0312714021522855,2.982958143090487,3.0023474672819073,3.0823968463139284,3.211306960327825,3.377147114821844,3.5717817493399875,3.792956274087117,4.0440306071095655,4.331506000414363,4.661125523639355,5.033875420737961,5.443528141051006,5.877137796448127,6.318610591196382,6.752408445607565,7.162662276861828,7.534546574258889,7.856879717904279,8.125702356901952,8.347877643233026,8.538428281527253,8.716348693460956,8.90043264998519,9.106212641065138,9.344322948960112,9.620083328812274,9.933935446416715,10.2823681088751,10.659039320328425,6.27844642083621,6.838197908976841,7.336492952235262,7.759293069005221,8.094721105632107,8.334279974014873,8.473935933703496,8.51479308851488,8.463018314518528,8.328677483379202,8.12331532253288,7.85663581216383,7.534243818020564,7.162087169947465,6.751797281449238,6.31819317767644,5.876761999238586,5.440646239867888,5.016658710756508,4.608847577000458,4.223462513482099,3.8706690243188526,3.563045284099769,3.312311428522833,3.125961577281321,3.005146496582162,2.9445998096114625,2.9347580880257307,2.965560233125756,3.0307735266085873,3.1311365710383186,3.273708665000218,3.4663398951172533,3.7116355303301907,4.003727652102242,4.328728559845956,4.668015928850581,5.0019620438802255,5.310807871940873,5.571166350775728,5.755595712473674,5.843236506809652,5.831022433483485,5.732600662125818,5.570491618065869,5.366717266061792,5.135570497466749,4.880951181295884,4.598784924678657,4.281999099036873],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=10","opacity":1.0,"showlegend":true,"visible":false,"x":[4.790397405221612],"y":[8.139446456560734],"type":"scatter"}],                        {"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}},"yaxis":{"range":[1,9],"title":{"text":"Gold Content"}},"xaxis":{"range":[-1,7],"title":{"text":"X"}},"title":{"text":"Gold Search"},"sliders":[{"active":0,"steps":[{"args":[{"visible":[true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"0"}],"label":"Ground Truth (f)","method":"update"},{"args":[{"visible":[true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"1"}],"label":"i=1","method":"update"},{"args":[{"visible":[true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"2"}],"label":"i=2","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"3"}],"label":"i=3","method":"update"},{"args":[{"visible":[true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"4"}],"label":"i=4","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"5"}],"label":"i=5","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"6"}],"label":"p=6","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"7"}],"label":"i=6","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"8"}],"label":"p=7","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"9"}],"label":"i=7","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"10"}],"label":"p=8","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"11"}],"label":"i=8","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"12"}],"label":"p=9","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"13"}],"label":"i=9","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"14"}],"label":"p=10","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,true,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"15"}],"label":"i=10","method":"update"}]}]},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>

### Cross Validation

In [41]:
# Extract the final model
model = cast(
    TorchModelBridge,
    not_none(ax_client.generation_strategy.model),
)
# Perform cross validation to estimate out of sample error.
cv = cross_validate(model)
diagnostics = compute_diagnostics(cv)
print_markdown(pd.DataFrame(diagnostics).to_markdown())

|      |   Mean prediction CI |      MAPE |     wMAPE |   Total raw effect |   Correlation coefficient |   Rank correlation |   Fisher exact test p |   Log likelihood |      MSE |
|:-----|---------------------:|----------:|----------:|-------------------:|--------------------------:|-------------------:|----------------------:|-----------------:|---------:|
| gold |             0.239113 | 0.0495505 | 0.0414965 |            1.62874 |                  0.938666 |           0.833333 |              0.166667 |          8.39369 | 0.293955 |

In [42]:
fig = interact_cross_validation_plotly(cv)
fig.update_layout(dict(width=None))
render_plotly_html(fig)

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="fbfd7029-0999-41fc-86d4-9e756e0e280d" class="plotly-graph-div" style="height:500px; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("fbfd7029-0999-41fc-86d4-9e756e0e280d")) {                    Plotly.newPlot(                        "fbfd7029-0999-41fc-86d4-9e756e0e280d",                        [{"hoverinfo":"none","line":{"color":"black","dash":"dot","width":2},"mode":"lines","showlegend":false,"visible":true,"x":[1.2709608779420252,8.770881714793267],"y":[1.2709608779420252,8.770881714793267],"type":"scatter"},{"error_x":{"array":[null,null,null,null,null,null,null,null,null],"color":"rgba(128,177,211,0.4)","type":"data"},"error_y":{"array":[1.8015391468374415,0.44462340504182923,0.4334904838895837,0.16954053183056034,1.4921744775166508,0.08763873122603702,0.05039194661615546,0.030598320552780223,0.08143566735225702],"color":"rgba(128,177,211,0.4)","type":"data"},"hoverinfo":"text","marker":{"color":"rgba(128,177,211,1)"},"mode":"markers","name":"In-sample","showlegend":true,"text":["\u003cb\u003eArm 0_0\u003c\u002fb\u003e\u003cbr\u003e\u003cbr\u003eActual Outcome: 5.058 [nan, nan]\u003cbr\u003ePredicted Outcome: 6.628 [4.827, 8.430]\u003cbr\u003e\u003cbr\u003e\u003cem\u003eParameterization:\u003c\u002fem\u003e\u003cbr\u003ex: 0.32872711926390363","\u003cb\u003eArm 1_0\u003c\u002fb\u003e\u003cbr\u003e\u003cbr\u003eActual Outcome: 5.092 [nan, nan]\u003cbr\u003ePredicted Outcome: 5.347 [4.903, 5.792]\u003cbr\u003e\u003cbr\u003e\u003cem\u003eParameterization:\u003c\u002fem\u003e\u003cbr\u003ex: 1.4348541948065263","\u003cb\u003eArm 2_0\u003c\u002fb\u003e\u003cbr\u003e\u003cbr\u003eActual Outcome: 5.703 [nan, nan]\u003cbr\u003ePredicted Outcome: 5.376 [4.942, 5.809]\u003cbr\u003e\u003cbr\u003e\u003cem\u003eParameterization:\u003c\u002fem\u003e\u003cbr\u003ex: 1.1448646473418669","\u003cb\u003eArm 3_0\u003c\u002fb\u003e\u003cbr\u003e\u003cbr\u003eActual Outcome: 5.777 [nan, nan]\u003cbr\u003ePredicted Outcome: 5.786 [5.616, 5.955]\u003cbr\u003e\u003cbr\u003e\u003cem\u003eParameterization:\u003c\u002fem\u003e\u003cbr\u003ex: 4.012995102221842","\u003cb\u003eArm 4_0\u003c\u002fb\u003e\u003cbr\u003e\u003cbr\u003eActual Outcome: 3.03 [nan, nan]\u003cbr\u003ePredicted Outcome: 3.104 [1.612, 4.596]\u003cbr\u003e\u003cbr\u003e\u003cem\u003eParameterization:\u003c\u002fem\u003e\u003cbr\u003ex: 2.451072738768894","\u003cb\u003eArm 5_0\u003c\u002fb\u003e\u003cbr\u003e\u003cbr\u003eActual Outcome: 6.431 [nan, nan]\u003cbr\u003ePredicted Outcome: 6.432 [6.344, 6.519]\u003cbr\u003e\u003cbr\u003e\u003cem\u003eParameterization:\u003c\u002fem\u003e\u003cbr\u003ex: 4.194693878482701","\u003cb\u003eArm 6_0\u003c\u002fb\u003e\u003cbr\u003e\u003cbr\u003eActual Outcome: 7.419 [nan, nan]\u003cbr\u003ePredicted Outcome: 7.42 [7.370, 7.471]\u003cbr\u003e\u003cbr\u003e\u003cem\u003eParameterization:\u003c\u002fem\u003e\u003cbr\u003ex: 4.491198145517794","\u003cb\u003eArm 7_0\u003c\u002fb\u003e\u003cbr\u003e\u003cbr\u003eActual Outcome: 7.746 [nan, nan]\u003cbr\u003ePredicted Outcome: 7.743 [7.713, 7.774]\u003cbr\u003e\u003cbr\u003e\u003cem\u003eParameterization:\u003c\u002fem\u003e\u003cbr\u003ex: 4.608163665936905","\u003cb\u003eArm 8_0\u003c\u002fb\u003e\u003cbr\u003e\u003cbr\u003eActual Outcome: 7.964 [nan, nan]\u003cbr\u003ePredicted Outcome: 7.972 [7.890, 8.053]\u003cbr\u003e\u003cbr\u003e\u003cem\u003eParameterization:\u003c\u002fem\u003e\u003cbr\u003ex: 4.699603014745402"],"visible":true,"x":[5.057664805217066,5.091532753266253,5.703244208949001,5.776814007863983,3.0295919107202014,6.431018758151026,7.41938481136026,7.746444938096204,7.964008751168905],"y":[6.6284370753716795,5.347301959124916,5.375900057595387,5.7858828106524465,3.1040408480428234,6.4315461328688,7.42024850247203,7.74319107980205,7.971890591826844],"type":"scatter"}],                        {"annotations":[{"showarrow":false,"text":"Show CI","x":1.125,"xanchor":"left","xref":"paper","y":0.9,"yanchor":"middle","yref":"paper"}],"height":500,"hovermode":"closest","showlegend":false,"updatemenus":[{"buttons":[{"args":[{"visible":[true,true]},{"xaxis.range":[1.2709608779420252,8.770881714793267],"yaxis.range":[1.2709608779420252,8.770881714793267]}],"label":"gold","method":"update"}],"x":0,"xanchor":"left","y":1.125,"yanchor":"top"},{"buttons":[{"args":[{"error_x.width":4,"error_x.thickness":2,"error_y.width":4,"error_y.thickness":2}],"label":"Yes","method":"restyle"},{"args":[{"error_x.width":0,"error_x.thickness":0,"error_y.width":0,"error_y.thickness":0}],"label":"No","method":"restyle"}],"x":1.125,"xanchor":"left","y":0.8,"yanchor":"middle"}],"xaxis":{"linecolor":"black","linewidth":0.5,"mirror":true,"range":[1.2709608779420252,8.770881714793267],"title":{"text":"Actual Outcome"},"zeroline":false},"yaxis":{"linecolor":"black","linewidth":0.5,"mirror":true,"range":[1.2709608779420252,8.770881714793267],"title":{"text":"Predicted Outcome"},"zeroline":false},"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}},"margin":{"b":90},"title":{"text":"Cross-validation"}},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>

## Bayesian Optimization

### Probability of Improvement (PI)
Choose next point based off the highest probability over the current max.


$$
\begin{align*}
x_{t+1} &= \arg\max_x P(f(x) \geq (f(x^+))) \\
& = \arg\max_x \Phi\big ( \frac{\mu_t(x) - f(x^+)}{\sigma_t(x)} \big )
\end{align*}
$$

In [43]:
generation_strategy = create_generation_strategy(
    botorch_acqf_class=ProbabilityOfImprovement
)
ax_client = create_client(generation_strategy=generation_strategy)
predictions, acquisitions = run_ax(n=10, ax_client=ax_client)
results["PI"] = ax_client.get_trials_data_frame()

[WARNING 08-11 10:42:39] ax.service.ax_client: Random seed set to 1. Note that this setting only affects the Sobol quasi-random generator and BoTorch-powered Bayesian optimization models. For the latter models, setting random seed to the same number for two optimizations will make the generated trials similar, but not exactly the same, and over time the trials will diverge more.
[INFO 08-11 10:42:39] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[RangeParameter(name='x', parameter_type=FLOAT, range=[0.0, 6.0])], parameter_constraints=[]).
[WARNING 08-11 10:42:40] ax.service.utils.report_utils: Column reason missing for all trials. Not appending column.


In [44]:
render_plotly_html(
    plot_surrogate_and_acquisition(
        x=x,
        y=y,
        ax_client=ax_client,
        gold_fn=gold,
        predictions=predictions,
        acquisitions=acquisitions,
        line_kwargs=get_line_kwargs(),
    )
)

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="c765331c-0260-4e9d-865f-80d7ae11e7a8" class="plotly-graph-div" style="height:100%; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("c765331c-0260-4e9d-865f-80d7ae11e7a8")) {                    Plotly.newPlot(                        "c765331c-0260-4e9d-865f-80d7ae11e7a8",                        [{"hoverinfo":"skip","mode":"lines","name":"Ground Truth (f)","showlegend":true,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[2.85,3.856123347536194,4.638417508253971,5.221510704359092,5.628898102467025,5.8829418136029314,6.00487089320169,6.01478134110787,5.9316361015757515,5.773265063269314,5.5563650592622364,5.296499867037907,5.008100208489416,4.7044637499195545,4.397755102040818,4.099005819975396,3.818114403255205,3.5638462958218278,3.343833886026604,3.1645765066304996,3.0314404348042556,2.948658892128277,2.919332044592691,2.9454270025973184,3.0277778209516644,3.166085498874992,3.3589179799961926,3.6037101523539157,3.896763848396514,4.233247844982003,4.607197863378097,5.011516569262348,5.4379735727217735,5.877205428253326,6.318715634763429,6.7508746355685645,7.1609198183944756,7.534955515376893,7.857953003061169,8.113750502402425,8.28505317876541,8.35343314192454,8.29932944606415,8.10204808977798,7.739762016069648,7.18951111235242,6.427202210449309,5.42760908659298,4.164372461425842,2.6100000000000705],"type":"scatter","xaxis":"x","yaxis":"y"},{"marker":{"size":10},"mode":"markers","name":"i=1","opacity":1.0,"showlegend":true,"visible":true,"x":[1.8140525221824646],"y":[4.153277647970732],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=2","opacity":1.0,"showlegend":true,"visible":true,"x":[5.636016067117453],"y":[6.4030358079544385],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=3","opacity":1.0,"showlegend":true,"visible":true,"x":[4.097510201856494],"y":[6.082020053347733],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=4","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.04806715789974354,0.038950223365649135,0.030354336396250188,0.022509385582449165,0.01565484471444161,0.010008710974654726,0.005719485323507537,0.0028074414473676745,0.0011187110567908807,0.00033445474097389756,6.763593052259173e-05,8.266832959809783e-06,5.831695418172122e-07,2.985012540800117e-08,2.491202025783452e-09,1.1707468232903512e-09,5.124717396995852e-09,8.585568213060402e-08,1.659421144300826e-06,2.0170013641916788e-05,0.0001388493685416449,0.0005912252445761788,0.0017531414190953476,0.0039971044449773774,0.007537595566893882,0.012382573513050206,0.018389243070984225,0.02537329167205872,0.033241721103364125,0.04215696674967249,0.05276737552157317,0.06653361719863721,0.08605825133743371,0.11490525041123252,0.1558616533909716,0.20776285815694495,0.26457331412072066,0.3189376814982125,0.366019099282582,0.40418801632713064,0.43375533297023466,0.4556737048276599,0.4707950554849367,0.479576388530276,0.4821189283174623,0.4785898253655618,0.46994527950710946,0.4582178737478434,0.44568195167095287,0.4338066248492031],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=4","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[5.879828741772096,5.723684944424338,5.564919034717484,5.405287615415519,5.246875209974377,5.092092146564724,4.943655173439945,4.804546034740408,4.677943045572257,4.567120898175266,4.4753146866562545,4.405545664614189,4.360408768005911,4.341825638785639,4.350771871227595,4.386993354512391,4.448748389221656,4.532810844813912,4.634893013277516,4.750143492373074,4.873588620047045,5.000504620600418,5.12671443494951,5.248806696645397,5.364276715061822,5.471590800773641,5.570176158374724,5.660339316717575,5.74311715203231,5.820066490320642,5.893001544577461,5.96369348171465,6.03355350613943,6.103329968324751,6.172860705100469,6.24095696127736,6.305593589211606,6.364345953453986,6.4148589511706895,6.45527159344706,6.484555617589533,6.502739129116825,6.51099724395559,6.511601248774515,6.50772643883592,6.503127171113509,6.501696264117567,6.50693847950454,6.521501446900843,6.547022552377477,6.101743942952618,6.170066285289676,6.219591383202151,6.250977680328067,6.2659653602492105,6.267250979972175,6.257994311081833,6.241256977277889,6.219539143177324,6.194444308974291,6.166489252021625,6.135068025432309,6.098571020386865,6.054651956833938,6.000626656609064,5.933977068904017,5.852922089199586,5.75696588950724,5.647101205867781,5.525598774378168,5.395669412032708,5.2610911299200485,5.125838350762745,4.993740002771914,4.868184535225848,4.751883097110591,4.646697269002982,4.553534562066633,4.472312966795951,4.401994655091324,4.340688005214141,4.285815939106026,4.234346690290113,4.183080205450835,4.128979247612083,4.069527932593617,4.003040362354105,3.928733988138434,3.8466290758021366,3.757397508226621,3.662195051125944,3.5624967627493516,3.4599483111916736,3.356240325414143,3.2530086498943227,3.1517603858862326,3.053823678413531,2.960318116876881,2.872142141022751,2.789973795802151],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=4","opacity":1.0,"showlegend":true,"visible":false,"x":[5.376579210943656],"y":[7.78026814236398],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=5","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.03270227567121766,0.02699984846732462,0.021605335096855312,0.016645775335546786,0.01224713736324175,0.008519159826573702,0.005535693919053022,0.003314228817432878,0.0018021351608542668,0.0008794277365751368,0.00038397629851540864,0.00015265943848391807,5.8378307113452185e-05,2.388250209303332e-05,1.2153796514674943e-05,8.90432277240389e-06,1.0011264030674819e-05,1.629988932331542e-05,3.346074355703932e-05,7.492737417722573e-05,0.000164820796343754,0.0003363574213714318,0.0006229168460518576,0.0010450875170578175,0.0016011853600457527,0.002266640928120571,0.0030023685229162646,0.0037686228199229313,0.004540322979693665,0.005321129056209206,0.006155246125739249,0.00713721089258916,0.008419872293406717,0.010217038120916306,0.012786108561788233,0.016363692147031886,0.021057945463689984,0.02674066846041739,0.03299832108694814,0.039201945586391396,0.044701388848710284,0.049093623527079105,0.05248475809260955,0.05563412203312857,0.05983911035537887,0.06648225453615765,0.07638454912165019,0.08933423717327743,0.10416035012235633,0.11935167318622429],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=5","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[7.495651257760675,7.284834873266803,7.066648672973573,6.843106579207252,6.616719721149,6.390513858849745,6.168023792794874,5.953256833214429,5.750616697632555,5.564779038074719,5.400510484652241,5.262425011981605,5.154675016004324,5.080580144516059,5.0422049366001085,5.039906630651957,5.071909162410016,5.134264322955848,5.221450663302278,5.327092357566368,5.444597336589617,5.567694335321278,5.69085997443865,5.80963297282226,5.920816446145916,6.022571306179688,6.114404639850731,6.197057358718479,6.272296172046842,6.342616873323181,6.410869842905653,6.479825268191519,6.551705345010836,6.627723635688087,6.707687178174618,6.789787685359177,6.870937771331512,6.947534691565976,7.0162211970593304,7.074519720757224,7.121287600760339,7.156963394743796,7.183594938519506,7.2046588613056555,7.224699072361968,7.248825258084782,7.282077289406204,7.328642314700801,7.391199689415242,7.4708353553172735,6.244371433637564,6.380361619600279,6.4857553812090085,6.558925988108057,6.599590092991258,6.608925920272547,6.5895898562198,6.545575313341296,6.481545809613815,6.402025221171347,6.310774782550063,6.210403359288035,6.1022279125734675,5.986384732490723,5.8621741298915735,5.728601597092776,5.5850568085970735,5.43200750549391,5.271317815118637,5.106074215983993,4.940227463057346,4.778168188253633,4.624291483562842,4.482590301250648,4.356304463717433,4.247642149406956,4.157583920461708,4.085775199382301,4.030510869208282,3.9888145543540365,3.9566143039828385,3.9290150310244236,3.9006654014728843,3.8662122993906496,3.8208291753302377,3.7607934114317016,3.68396730695931,3.589827927557511,3.4791971757993863,3.353918972676915,3.216537498561446,3.070003181522298,2.917421925272162,2.7618543050479074,2.60616517081994,2.452919983933062,2.304321847045188,2.1621821280418287,2.027917433249126,1.902566130487723],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=5","opacity":1.0,"showlegend":true,"visible":false,"x":[6.0],"y":[2.6100000000000705],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=6","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.08653692470322279,0.08156056891101435,0.07625600182025259,0.07065389706779239,0.06480464613287185,0.0587824508630282,0.05268861264445879,0.04665279448677954,0.04083065378889843,0.03539627440546545,0.03052878913022684,0.026394888010511496,0.023132125566322995,0.020840002602230068,0.019583400019066766,0.019404299698161744,0.020327254734751176,0.02235412696439887,0.025455591003541878,0.029553476554349194,0.034507519618515815,0.040118901403697116,0.04614988225923302,0.05235081942124289,0.05848558461157401,0.06435048346958634,0.06978598681967643,0.07468283604617043,0.07898427535806345,0.08268491609948829,0.08582466436187419,0.08847384204779118,0.09070411766668868,0.09254093313601472,0.09389891475116421,0.09451989938665824,0.09397788859387556,0.09176573020313501,0.08741953273970508,0.08066118295517602,0.07154360270953186,0.06056901643391124,0.048715657369874474,0.03728086441426747,0.02750731428417421,0.02015074518290084,0.015299190652774032,0.012574766288612716,0.011489487218403602,0.011674051234425921],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=6","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[10.101835960966621,9.888198543890951,9.658238360386132,9.413302160952702,9.155530794462443,8.887974501659706,8.614685118088907,8.340767220703402,8.072365901422021,7.816564956560724,7.581166724830069,7.374324846263104,7.204005499591133,7.077263151984627,6.999335443308955,6.972589683391676,6.995440643965557,7.062060768490481,7.1634897961014286,7.289016474941914,7.427384067775535,7.567778983479824,7.700595295745157,7.817984728305926,7.914209922374786,7.985820110038006,8.031664922398372,8.052756291079934,8.051982554324107,8.033675252211943,8.003030056982594,7.965391271459723,7.925426649291417,7.886247531698084,7.848568726133738,7.810169967018549,7.766448613141656,7.711849341365584,7.641270062929096,7.551206099982584,7.440549475902452,7.311004421531266,7.167118419863434,7.015963409686333,6.866537131647981,6.728990922048703,6.613818246371373,6.531031681013244,6.489307994101274,6.495224227837332,3.815503019839656,4.0809396964228135,4.304558188312066,4.482725761700065,4.6138023051215145,4.69871999165364,4.741075711789359,4.7468742272226665,4.723370563258119,4.677625501050517,4.615369116335052,4.5402741587391775,4.453684452510247,4.354813161767793,4.2413946899107575,4.110739339958814,3.961098652757516,3.7930898458419375,3.6102244965341526,3.4183176537896034,3.2246115332378413,3.036878561704627,2.8625930748560178,2.708222418217258,2.5786606598239565,2.476811301509039,2.403317709886214,2.356439183734948,2.3320742021732315,2.32393809210235,2.3239078118235215,2.322549462152106,2.3098421621876515,2.276102815258609,2.213098356695345,2.115298577007507,1.980875611665316,1.8114876852392126,1.6113535627061921,1.3863243960311729,1.1430722616705222,0.8884345636341697,0.628924339739577,0.3703968690397721,0.11785164114969238,-0.12465624018448196,-0.3540217596326851,-0.5680372487365588,-0.76530213301512,-0.9451120541456515],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=6","opacity":1.0,"showlegend":true,"visible":false,"x":[4.298252484395651],"y":[6.794103154945049],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=7","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.08966711190983648,0.0842240898112912,0.07825853154207962,0.07177966454016985,0.06482502050886371,0.057471192200251174,0.04984554335982533,0.04213629767798683,0.03459592091769693,0.027529941445981625,0.021262858109987817,0.01607959916941694,0.012159259025743625,0.00953995465955167,0.008152871830216972,0.007918771523477896,0.008839496903553465,0.011015960964133287,0.014578439364465956,0.019561140321556557,0.025811943807240504,0.032994106460401525,0.040659041214327014,0.04833394718545018,0.055585606056830994,0.06205265534159303,0.06745679517776089,0.07160790895689552,0.07441660938663533,0.07592502427606128,0.07636223734110324,0.07621890092762741,0.07630586653781592,0.07770768284392211,0.08148684044486078,0.08805973531424963,0.09656662879266104,0.10478354100566839,0.10982047848773038,0.10913104532755497,0.10126638168116592,0.08634064086687995,0.06635092503035518,0.045083942060355674,0.0269096841154058,0.014535677176743566,0.007746027514372361,0.004623898782483069,0.0034354351972235566,0.0032671894432677135],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=7","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[10.359563100177485,10.127498033751957,9.869344942840137,9.585324437239965,9.276787700662512,8.946513041659006,8.599000469567262,8.240730341349234,7.8803377118391955,7.528638211620608,7.198426139270717,6.903954599409793,6.660006520389638,6.480481930894404,6.376470129328743,6.353853621898401,6.410725134348763,6.536579382788979,6.714734303173941,6.925328685900739,7.147836799271177,7.363026640280124,7.554386998026512,7.7090932524243625,7.818595449166712,7.878902850195951,7.890615194159141,7.858719575410986,7.792139495798914,7.702995435984315,7.605521195333904,7.514585763715643,7.443806724663824,7.403318389337388,7.397383122698253,7.422426568058149,7.467116795663586,7.51458311380571,7.54606007108933,7.544655547871142,7.4982472083196905,7.401257324841062,7.255257660480019,7.068510485358868,6.854702789775962,6.631279530868436,6.417798762565178,6.2343236439524095,6.099718106292093,6.029899921350274,3.84371956224354,4.220445870713744,4.552034818879386,4.832622361275633,5.058917118936161,5.231691829150014,5.356270455073464,5.442191355741292,5.500592805710253,5.5408318477811465,5.567916775337429,5.581126012907654,5.573993431210562,5.535708846895811,5.453844626170821,5.318117421568003,5.123909996012092,4.873960345330927,4.57809652206335,4.251272874138155,3.9112510570126013,3.576450281151235,3.2641486951690046,2.989094362389832,2.762508161283289,2.5914253600409713,2.4783173897096704,2.4209503871583404,2.4124639050219296,2.44168481732228,2.493721681855289,2.550907271036703,2.594164317608307,2.604853306096338,2.567113089318842,2.4706051044974533,2.3127094092004232,2.0978559072765672,1.8352404096721253,1.5366565191912565,1.214727978718305,0.8816049333962352,0.5481056658823338,0.22323921050011553,-0.08597458769778488,-0.3744718152207849,-0.638972847083898,-0.8777331072926522,-1.0902620803742984,-1.2770426796645715],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=7","opacity":1.0,"showlegend":true,"visible":false,"x":[4.702762526338227],"y":[7.97083381305886],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=8","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.15521959126548893,0.15300862259666823,0.1498826857563066,0.1455675425534418,0.13971873073080796,0.13190784693637497,0.1216136605503268,0.10823421265700107,0.09116477917877698,0.07006016762213087,0.04556540246919751,0.020980694301082417,0.004047759051219702,3.605164637933026e-05,4.1567441753608643e-17,1.0593636629076215e-98,6.660105530183806e-10,0.00023876872362523017,0.0055125785760729825,0.01914927513793499,0.03524630973460835,0.048846504410500015,0.05798188133899445,0.06222820190091103,0.061730239720895516,0.056823128632072076,0.047987480091922316,0.036028498241639076,0.022468365445896678,0.010020481326018146,0.002211174097759848,8.154814061963776e-05,8.094382155404229e-09,1.0184514870575887e-23,2.0735509286007857e-43,8.201398951485256e-20,8.181237148992037e-07,0.006622890189304626,0.22018749303211074,0.7766985776605184,0.8719450775495452,0.8828395506071974,0.8747505088602466,0.7675836036468769,0.07706053288242017,8.632509787514815e-10,5.5063984338751604e-31,2.3751138495285948e-58,1.0399303993859618e-129,1.2320065118431594e-270],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=8","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[21.676767258261275,21.13005010660933,20.454106138339977,19.630228382844418,18.64188555062205,17.477365970523742,16.13325566358391,14.618691472232442,12.960115697139818,11.205929377755103,9.429988090309912,7.732334911334418,6.235019858489645,5.070530931631973,4.360634453255586,4.1848129200711845,4.542246634697611,5.338225903338655,6.417702143666762,7.605027521121874,8.733373261191389,9.663690634564004,10.295251260791769,10.570328353161335,10.475208035048325,10.038880107409607,9.32975099367756,8.449759413513647,7.5245633818101565,6.688294829562247,6.0621854960281745,5.728730527976311,5.707443981439658,5.944233517399304,6.330578464923357,6.761760686418145,7.185747196804042,7.5652248362256325,7.878459749674508,8.141286956072545,8.34975529575322,8.449524112601505,8.391164171796682,8.16947882569555,7.79040776259195,7.212189738273538,6.372883189533406,5.2755655560944,3.994941501785359,2.6816171467164875,2.635883356614943,3.9402241307523242,5.218037056351114,6.333415035215678,7.179042556707615,7.750958576386673,8.080508893850348,8.220960904628257,8.24771616703707,8.204341616494432,8.075807039953354,7.8345431375730294,7.5030683035955485,7.128094420820124,6.724842433250822,6.301676422582003,5.8580666113226805,5.330618521492264,4.633876754104501,3.723138711398944,2.6185036646415423,1.3976413945911466,0.17385906593975609,-0.9282046384865223,-1.7929809124448939,-2.328636776283364,-2.4765803064566168,-2.21721804369158,-1.5732264381658414,-0.6109006851940366,0.5608111213768452,1.7949866594156485,2.917364337528333,3.745562760553157,4.119007994667209,3.939537525191551,3.20578035555236,1.9990126284722205,0.4440267413489343,-1.3231968477269893,-3.1771229122116917,-5.014504098519572,-6.758701335648006,-8.359003679809714,-9.787130980745115,-11.032547218916012,-12.09765581224364,-12.993489720176054,-13.73617619609674,-14.344239036888343],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=8","opacity":1.0,"showlegend":true,"visible":false,"x":[5.0411465101047845],"y":[8.353438586358578],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=9","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.14057140027303994,0.13779745226525306,0.13394958665715567,0.12875386869528815,0.12188055708770378,0.11294280637673919,0.10151172627208697,0.08717429285343327,0.06969537747152607,0.04941381731652445,0.028077875122818143,0.010018639905387074,0.0010799011751257339,1.461023140568827e-06,3.938663948735982e-25,1.824e-320,5.103269968946312e-14,1.09794504426673e-05,0.0009774289352789192,0.005572545047319623,0.012811663668895416,0.019640774003510966,0.024054633788159533,0.02530571018127387,0.023439502541747315,0.019013694270409588,0.013031669420115957,0.006940352120025311,0.002392738093842317,0.00034754164901230385,6.5544696450423385e-06,2.653698870018376e-10,1.7389607944820187e-26,3.3637362315297265e-136,1.9170174956089534e-308,2.1543128149450002e-163,7.083475480745266e-48,3.8960315423158356e-19,8.413894836327964e-14,0.0001807590842291199,0.18418313013499454,0.4792249577501559,0.19743594053581043,0.00023752901322700732,8.238590173674814e-25,4.598522789451187e-79,1.938902660200601e-232,3.575330419809842e-243,0.0,0.0],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=9","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[25.259279637305617,24.2681398955971,23.118464028451026,21.802684282482122,20.319254682963336,18.675025873461315,16.887824747587743,14.989001780088284,13.025563857912767,11.061336790680393,9.17641797061728,7.464024816426813,6.023786908829072,4.950673566473523,4.31923262351829,4.163786293447482,4.457720120933229,5.108981231019396,5.983172272290577,6.931036097174712,7.810910445883848,8.50534819462837,8.932144909477003,9.050404322515584,8.86227104515902,8.410729183003497,7.773568477696699,7.053417225647296,6.363803289167308,5.811715285562368,5.478272799007309,5.400962112097046,5.563228180124054,5.899027916899841,6.318518553035727,6.751329795548127,7.168274448742352,7.545511658824005,7.8640576477575825,8.119158692218882,8.290639073596079,8.35396148584117,8.298654724510103,8.107304650335665,7.7591753513505175,7.214682387509611,6.409812943794079,5.327816941531594,4.025772663152058,2.6254831684652546,2.617738078973122,4.00699498456494,5.311196762498126,6.402647254495368,7.207288472872945,7.752332361193847,8.096960851721862,8.288804707628882,8.34658966562037,8.279001222379737,8.110196250024686,7.855081274174915,7.528541272154949,7.154740007501571,6.744368657424349,6.3126195368593105,5.8792991310013685,5.416888356029184,4.862647479487956,4.164818040654351,3.312107942227911,2.341055428180844,1.327667643598471,0.3711213658660828,-0.4245406220638239,-0.9671490046362785,-1.1898857773858427,-1.0609570766533993,-0.5894406236811682,0.17264268835616825,1.1321820576524786,2.1612008492325123,3.1081318329227074,3.814833031691772,4.139657093627043,3.9858481343990495,3.325456268954638,2.1942997792450023,0.6701390905295477,-1.1479563269855015,-3.1559356202026096,-5.256212699744948,-7.364608106503526,-9.413634828089926,-11.35311009605179,-13.149009757447564,-14.78132108551292,-16.241461704932835,-17.529655301656096,-18.65250714228062],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=9","opacity":1.0,"showlegend":true,"visible":false,"x":[5.026932150430952],"y":[8.353817966113354],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=10","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.14154904985138048,0.1387805059353558,0.13491701613960883,0.12968129797321126,0.12273972915011931,0.11370117817242796,0.10213272109122597,0.08761951436868819,0.06993173615673892,0.049431358541478565,0.027925149965326294,0.009839116734003443,0.0010251919035459474,1.2084589100990427e-06,4.9854972494630023e-26,0.0,1.8523331101717738e-14,8.011076712266022e-06,0.0008064988933324129,0.004789533037761709,0.011172987120841619,0.01715872423734896,0.020865915582596532,0.02161293759300807,0.019509752890095024,0.015196671980499855,0.009761917955149019,0.0046616624089942955,0.0013154684464908653,0.00012568862710041575,8.150162093848098e-07,7.717128103609637e-13,1.592749164451241e-39,0.0,0.0,0.0,1.6168730012706332e-112,1.4676031889494119e-33,6.037740554410893e-54,6.894643974407606e-11,0.09624154143378379,0.5077161454343713,0.06882114071635284,1.478039220273286e-09,9.38931942743258e-204,4.456855037948351e-208,0.0,0.0,0.0,0.0],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=10","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[26.01604592381915,24.931670154468566,23.685050425374754,22.27088960136458,20.6904234110325,18.953691970488812,17.081927940727645,15.109812461865243,13.087217578411053,11.079901525238697,9.168470417223904,7.4448042854301795,6.0051297924255,4.9390987310061405,4.314718639941113,4.159897681198105,4.443641056615254,5.072686567949753,5.913835602330264,6.820407763673872,7.6540572004652345,8.301094222784316,8.683398472838565,8.764378471237976,8.5504619642585,8.088434478233165,7.458730745441389,6.764678348163916,6.117855537812858,5.620322142159742,5.345656794922937,5.322513320513885,5.526490976760355,5.8874125030153515,6.316888356463582,6.750541045079652,7.1650624360686725,7.53986006963215,7.858583968129062,8.117462983162792,8.292452851195844,8.35435006880882,8.29110322842802,8.091031665659767,7.744444377362302,7.214781784171525,6.426424003565192,5.3507111618180785,4.039904947946278,2.6116927830252403,2.610903852194673,4.027920671093662,5.342866753003391,6.425649615478315,7.212032799507926,7.743641562282208,8.087049736455814,8.28731553422435,8.35387935191834,8.287666131675245,8.114719136355259,7.856512316944115,7.530577519016996,7.159458829672482,6.749736569429556,6.3150887702727365,5.881522933057022,5.430164690028635,4.902161599192713,4.243510759516059,3.436459058569074,2.509647580682308,1.5320898581065139,0.5982548529613156,-0.18981114306208235,-0.7395004805038039,-0.9817766524695966,-0.8815928993398185,-0.44437524718827115,0.2814814655107165,1.2062575107090292,2.2050576017762102,3.129001507744449,3.82196945340087,4.143058740415807,3.9939713209994703,3.342176551335903,2.217006373887889,0.6897208392268768,-1.145796759043133,-3.1886976740436825,-5.342483902797718,-7.522188223753985,-9.658098361264791,-11.696872716857126,-13.60087205068788,-15.346410157401827,-16.921469352515082,-18.32327088455077,-19.555955416217756],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=10","opacity":1.0,"showlegend":true,"visible":false,"x":[5.022322927162973],"y":[8.353582242638396],"type":"scatter"}],                        {"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}},"xaxis":{"anchor":"y","domain":[0.0,0.98],"matches":"x2","showticklabels":false,"range":[-1,7],"title":{"text":"X"}},"yaxis":{"anchor":"x","domain":[0.575,1.0]},"xaxis2":{"anchor":"y2","domain":[0.0,0.98],"range":[-1,7]},"yaxis2":{"anchor":"x2","domain":[0.0,0.425]},"annotations":[{"font":{"size":16},"showarrow":false,"text":"Surrogate","textangle":90,"x":0.98,"xanchor":"left","xref":"paper","y":0.7875,"yanchor":"middle","yref":"paper"},{"font":{"size":16},"showarrow":false,"text":"Acquisition","textangle":90,"x":0.98,"xanchor":"left","xref":"paper","y":0.2125,"yanchor":"middle","yref":"paper"}],"title":{"text":"Gold Search"},"sliders":[{"active":0,"steps":[{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"0"}],"label":"i = 0","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"4"}],"label":"i = 1","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"7"}],"label":"i = 2","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false],"title":"10"}],"label":"i = 3","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,true,true,true,false,false,false,false,false,false,false,false,false],"title":"13"}],"label":"i = 4","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,false,false,true,true,true,true,false,false,false,false,false,false],"title":"16"}],"label":"i = 5","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,false,false,true,false,false,true,true,true,true,false,false,false],"title":"19"}],"label":"i = 6","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,false,false,true,false,false,true,false,false,true,true,true,true],"title":"22"}],"label":"i = 7","method":"update"}]}]},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>

### Expected Improvement (EI)
Choose the next point that has the highest expected improvement over the current max.

$$
\begin{align*}
x_{t+1} &= \arg\max_x \mathbb E[\max\{0, h_{t+1}(x) - f(x^+)\}] \\
&= (\mu_t(x) - f(x^+))\Phi(Z) + \sigma_t(x)\phi(Z) \\ 
Z &= \frac{\mu_t(x) - f(x^+)}{\sigma_t(x)}
\end{align*}
$$

In [45]:
generation_strategy = create_generation_strategy(
    botorch_acqf_class=ExpectedImprovement,
)
ax_client = create_client(generation_strategy=generation_strategy)
predictions, acquisitions = run_ax(n=10, ax_client=ax_client)
results["EI"] = ax_client.get_trials_data_frame()

[WARNING 08-11 10:42:40] ax.service.ax_client: Random seed set to 1. Note that this setting only affects the Sobol quasi-random generator and BoTorch-powered Bayesian optimization models. For the latter models, setting random seed to the same number for two optimizations will make the generated trials similar, but not exactly the same, and over time the trials will diverge more.
[INFO 08-11 10:42:40] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[RangeParameter(name='x', parameter_type=FLOAT, range=[0.0, 6.0])], parameter_constraints=[]).
[WARNING 08-11 10:42:41] ax.service.utils.report_utils: Column reason missing for all trials. Not appending column.


In [46]:
render_plotly_html(
    plot_surrogate_and_acquisition(
        x=x,
        y=y,
        ax_client=ax_client,
        gold_fn=gold,
        predictions=predictions,
        acquisitions=acquisitions,
        line_kwargs=get_line_kwargs(),
    )
)

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="1c8fe25e-8182-4434-9933-8a3830094906" class="plotly-graph-div" style="height:100%; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("1c8fe25e-8182-4434-9933-8a3830094906")) {                    Plotly.newPlot(                        "1c8fe25e-8182-4434-9933-8a3830094906",                        [{"hoverinfo":"skip","mode":"lines","name":"Ground Truth (f)","showlegend":true,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[2.85,3.856123347536194,4.638417508253971,5.221510704359092,5.628898102467025,5.8829418136029314,6.00487089320169,6.01478134110787,5.9316361015757515,5.773265063269314,5.5563650592622364,5.296499867037907,5.008100208489416,4.7044637499195545,4.397755102040818,4.099005819975396,3.818114403255205,3.5638462958218278,3.343833886026604,3.1645765066304996,3.0314404348042556,2.948658892128277,2.919332044592691,2.9454270025973184,3.0277778209516644,3.166085498874992,3.3589179799961926,3.6037101523539157,3.896763848396514,4.233247844982003,4.607197863378097,5.011516569262348,5.4379735727217735,5.877205428253326,6.318715634763429,6.7508746355685645,7.1609198183944756,7.534955515376893,7.857953003061169,8.113750502402425,8.28505317876541,8.35343314192454,8.29932944606415,8.10204808977798,7.739762016069648,7.18951111235242,6.427202210449309,5.42760908659298,4.164372461425842,2.6100000000000705],"type":"scatter","xaxis":"x","yaxis":"y"},{"marker":{"size":10},"mode":"markers","name":"i=1","opacity":1.0,"showlegend":true,"visible":true,"x":[1.8140525221824646],"y":[4.153277647970732],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=2","opacity":1.0,"showlegend":true,"visible":true,"x":[5.636016067117453],"y":[6.4030358079544385],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=3","opacity":1.0,"showlegend":true,"visible":true,"x":[4.097510201856494],"y":[6.082020053347733],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=4","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.020387547294865707,0.015366768246353711,0.011042261234807756,0.007475513868284752,0.004692700060572605,0.0026729556257204003,0.0013407389506664192,0.0005679654410395972,0.000191652296832379,4.752959392155687e-05,7.808256260199064e-06,7.616091964912769e-07,4.255818513706739e-08,1.753443162904469e-09,1.2453468890936949e-10,5.4997700724870385e-11,2.537398675255238e-10,4.887853162516092e-09,1.131736462003843e-07,1.6558174847095385e-06,1.3513995542381337e-05,6.66243450772157e-05,0.0002228079363727343,0.0005581265389956207,0.0011277791080561098,0.0019389466244205227,0.002947960178436996,0.004080876173158875,0.005269082796720898,0.006493205253905086,0.007834111184501695,0.009536017602725417,0.01208680247897304,0.01628527096024659,0.023143965337439544,0.03339436352522444,0.04680085581598082,0.06201065612262954,0.07711786374848693,0.09035715099549944,0.10049069960765333,0.1069162555707797,0.10966655075737554,0.10940319013884739,0.10740742906764404,0.10546089214024584,0.10543677634159627,0.10860927306421563,0.11518377666651884,0.12451909201655227],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=4","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[5.879828741772096,5.723684944424338,5.564919034717484,5.405287615415519,5.246875209974377,5.092092146564724,4.943655173439945,4.804546034740408,4.677943045572257,4.567120898175266,4.4753146866562545,4.405545664614189,4.360408768005911,4.341825638785639,4.350771871227595,4.386993354512391,4.448748389221656,4.532810844813912,4.634893013277516,4.750143492373074,4.873588620047045,5.000504620600418,5.12671443494951,5.248806696645397,5.364276715061822,5.471590800773641,5.570176158374724,5.660339316717575,5.74311715203231,5.820066490320642,5.893001544577461,5.96369348171465,6.03355350613943,6.103329968324751,6.172860705100469,6.24095696127736,6.305593589211606,6.364345953453986,6.4148589511706895,6.45527159344706,6.484555617589533,6.502739129116825,6.51099724395559,6.511601248774515,6.50772643883592,6.503127171113509,6.501696264117567,6.50693847950454,6.521501446900843,6.547022552377477,6.101743942952618,6.170066285289676,6.219591383202151,6.250977680328067,6.2659653602492105,6.267250979972175,6.257994311081833,6.241256977277889,6.219539143177324,6.194444308974291,6.166489252021625,6.135068025432309,6.098571020386865,6.054651956833938,6.000626656609064,5.933977068904017,5.852922089199586,5.75696588950724,5.647101205867781,5.525598774378168,5.395669412032708,5.2610911299200485,5.125838350762745,4.993740002771914,4.868184535225848,4.751883097110591,4.646697269002982,4.553534562066633,4.472312966795951,4.401994655091324,4.340688005214141,4.285815939106026,4.234346690290113,4.183080205450835,4.128979247612083,4.069527932593617,4.003040362354105,3.928733988138434,3.8466290758021366,3.757397508226621,3.662195051125944,3.5624967627493516,3.4599483111916736,3.356240325414143,3.2530086498943227,3.1517603858862326,3.053823678413531,2.960318116876881,2.872142141022751,2.789973795802151],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=4","opacity":1.0,"showlegend":true,"visible":false,"x":[6.0],"y":[2.6100000000000705],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=5","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.09547155548148073,0.09012315367766023,0.08453948709746592,0.0787720664398825,0.0728881073413244,0.06697131832618429,0.06112171615641685,0.055454102773951235,0.05009491192355703,0.04517736368719812,0.04083529291677101,0.037196584830153166,0.034377586739854055,0.03247961967305596,0.03158713259346367,0.031763954144298466,0.033041616130494215,0.03540611640048351,0.038794872713660465,0.043093464203219016,0.04813429950004522,0.05370241453782443,0.05954889924604401,0.06540920317770327,0.07102273976886013,0.07615099584494331,0.08059256879159914,0.08419441901129032,0.08685889241837394,0.08854583946417775,0.08926872452821076,0.0890834100755615,0.08806885906321629,0.08630084524699297,0.08382299663181395,0.08062595053736829,0.07665853287522406,0.07186878513802215,0.06624980256540197,0.059877598921278995,0.05293279281664019,0.04570038845225446,0.03854433060017129,0.031857471444034065,0.025995162876749578,0.0212112005623313,0.017621453620349697,0.015212767362008174,0.013892070981472354,0.013547350311460243],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=5","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[8.468340204355687,8.319943402601783,8.162103186435765,7.995976068123989,7.823209376135191,7.645993524155708,7.467096662943996,7.289871876069473,7.118225242618438,6.9565316542639515,6.809484676401886,6.681867568229242,6.578235548940744,6.502505318316022,6.45745742886477,6.444170668648828,6.46145175268706,6.50569541071989,6.571495854392652,6.652408258291769,6.741622037602594,6.832523214153313,6.919139358810739,6.996468946138988,7.060701564171072,7.109336896755312,7.141209674344048,7.156425913745337,7.15621380429822,7.142691623430785,7.118556170748796,7.08669948415421,7.049770027996924,7.009707752544808,6.967300495386683,6.921885338350014,6.871562949633711,6.813846969790884,6.746346899355913,6.667371194662391,6.576404009663911,6.474425803939747,6.364060807091803,6.249544059739751,6.1365090223222944,6.031605268918414,5.941965861532494,5.874557492559809,5.835499974628444,5.8294539833374905,3.2724665946977454,3.4182967608792794,3.538823744584498,3.6342758575024776,3.706475543289276,3.7587991609158076,3.7955038902761644,3.820904419579552,3.838698211626939,3.8514758746081603,3.8604331269947023,3.865292100258253,3.864432497103712,3.855226161379832,3.8345602474380462,3.799522864928596,3.7482098110946405,3.680520197123244,3.5983718296197003,3.5052437617572867,3.40558711057715,3.304251191484301,3.205964912551628,3.1148964345447103,3.0343019525139363,2.966266870760491,2.911539022681024,2.869452968801623,2.8379457197751607,2.813666396287744,2.7921842861264805,2.768300427512023,2.736466194054345,2.6913074394014487,2.6282439610554027,2.5441780047790177,2.438045091795591,2.310720828619293,2.164546499486759,2.0028420939693357,1.8294693544129985,1.6484675080219744,1.4637701617226218,1.2790017289428839,1.0973454043894808,0.9214713725059718,0.7535128138303064,0.5950776265320101,0.44728501457652126,0.3108177663392855],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=5","opacity":1.0,"showlegend":true,"visible":false,"x":[0.0],"y":[2.85],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=6","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.0016156939514402062,0.0015020946828143617,0.001476951285408289,0.0015261094636664536,0.0016397834433463313,0.0018107938998608054,0.0020334092156318842,0.002303322538474272,0.0026188714192503016,0.0029832847700624002,0.003407562652365493,0.0039135711677260755,0.004536976148070978,0.005329536910577491,0.00635976697582091,0.007709885013455654,0.009465899789841742,0.011701760416568964,0.014464087284184355,0.017758950990433092,0.021543474585033837,0.025724982399300517,0.030167932034265366,0.03470668872617749,0.03916124552260405,0.04335319684833069,0.047120052266985284,0.05032675521508602,0.05287373880842449,0.054700971316898314,0.05578737362876173,0.05614501115902364,0.0558079218180883,0.05481663709245247,0.053201399240772815,0.05097072897762422,0.048119125606985856,0.044652202438302514,0.04061391979588341,0.03610716607905464,0.031301628871729506,0.026425029072346187,0.02173672612183378,0.017487234207159478,0.013873454503077113,0.011004926227529549,0.008895683454675363,0.007485619177898257,0.006680022156266285,0.006387424430193112],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=6","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[4.905908659808474,4.883643161404619,4.8817389891275385,4.897101983347304,4.926080698629625,4.964983663622537,5.010500342949675,5.060015090275039,5.111809104127176,5.165149156251933,5.220264192760564,5.278212672128369,5.340645688643097,5.409474511093833,5.486456957594952,5.572725440745373,5.668305399876559,5.7718853385236,5.881050737228021,5.992660909113121,6.103220658104033,6.209216974127871,6.307403930892759,6.395027181827009,6.469984984075921,6.530925828558005,6.577284111170234,6.609255552088237,6.627713995373938,6.634071544604074,6.630085453354766,6.617618507777067,6.59836543433898,6.573566510789392,6.543741045470279,6.508518397475282,6.466784135930759,6.417092020056604,6.35810101126255,6.2889653171373,6.209645467959559,6.12111938534537,6.0254810188553,5.925920932299997,5.826589143454272,5.732346580283711,5.648418488932788,5.579971472396698,5.531651619914407,5.507115466729512,3.442968390844645,3.575525456808435,3.689188863350435,3.7836872140412074,3.859898985688348,3.919862675682658,3.9663067737429736,4.002064471623041,4.029594985543918,4.0506358588043945,4.065996658066315,4.0754987491742884,4.0780609904946346,4.071926476035696,4.055019913829902,4.025417950477458,3.9819051798817346,3.9245255488821797,3.854728334922411,3.775045490646841,3.6886833805398527,3.599129406635324,3.509799451582297,3.4237416470447597,3.343404355451953,3.2704713050949312,3.2057641982972576,3.149212220722484,3.0998880203102543,3.056110171285135,3.0156121602578816,2.9757767993941773,2.9339319883429793,2.887698323073371,2.8353708808680693,2.776304656452756,2.711157675138022,2.6416782506286536,2.5702433614054576,2.499403308588491,2.431480639973862,2.36824565351417,2.3106821478871553,2.2588510232153025,2.2118554301783346,2.167908596765405,2.124503240251161,2.078678595305866,2.027376678928827,1.9678729118472071],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=6","opacity":1.0,"showlegend":true,"visible":false,"x":[3.7965335580594815],"y":[5.013611148163598],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=7","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.0005283532403099045,0.00048299732584098065,0.00047125507956924476,0.00048730946707455845,0.0005277517246496629,0.0005905449762644241,0.000674274524185547,0.0007778637374438102,0.0009008234783435334,0.0010439913820867843,0.0012106179349094532,0.0014076033647843517,0.0016466799977679716,0.001945303257500277,0.0023268469818069834,0.002819295208452804,0.003451145900209033,0.004244812394913112,0.005210147085247399,0.006338775323406302,0.0076006716962570935,0.00894461408564047,0.010303099043397207,0.011601059469603882,0.012766823914898515,0.013743377397508331,0.014497999082504057,0.015028539808348765,0.015364834336469076,0.015564053828300721,0.015699335578787083,0.015841908328514447,0.016038376051869203,0.016290452352754708,0.016548676485245637,0.016718804285812197,0.01668206989363889,0.01632630335384538,0.01557737673103757,0.014422142354260889,0.012916879089619247,0.011178958832088205,0.009363384564685606,0.00762987117652969,0.006109811919036718,0.004883932636214662,0.003978119547455646,0.003376780177627304,0.0030450755938535245,0.002948992543031849],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=7","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[4.5684466272314745,4.555117899206872,4.558076057018069,4.575026254384327,4.603236177709414,4.639906790496799,4.682473126829002,4.728827867715111,4.777464444987706,4.827539237558198,4.8788544004703684,4.931764564397158,4.987012712529612,5.045503618672188,5.108027824436347,5.174955458111631,5.245936821124397,5.319784003208837,5.394666234315999,5.468399404338625,5.538727979538544,5.603576119127385,5.661253388454609,5.71060601614968,5.751108506363404,5.782892881891758,5.806714422726894,5.823854109574371,5.835959752319554,5.844830629655051,5.852154943233817,5.85921582035776,5.866592988950883,5.873970947870852,5.880199131129726,5.883476510875628,5.881624396551974,5.87242570814218,5.853954462358419,5.824860492940233,5.784589452701239,5.733525500837681,5.67304984087915,5.605512825679806,5.534121343446785,5.462747345417814,5.395668195273985,5.337254517526978,5.291611471784249,5.262162167396656,3.6752712817560966,3.794507787232929,3.9014258348418602,3.995766218514203,4.078111058231951,4.149907386245252,4.213102147990471,4.269682342182964,4.3212952880716315,4.36896727578085,4.4129286717067435,4.452549826255212,4.486389049159393,4.512350986133621,4.527950279325532,4.530670798636689,4.51840456358776,4.489916288910697,4.445096789634493,4.384969270340802,4.311591058515114,4.227769074318627,4.136704931827135,4.041661581683777,3.945674608787188,3.8513211151289317,3.7605532079839796,3.674599065409801,3.593932055835686,3.5183069029221006,3.446860770111778,3.3782757300021795,3.3109967560201357,3.2434956094994334,3.174565509885193,3.103622930141228,3.0309149097952846,2.957413568760927,2.884529084178107,2.8138137340869056,2.7466933213004134,2.6842446145848937,2.6270309455640777,2.575003291088608,2.527470831910983,2.4831425914095626,2.440239677340136,2.396675212674867,2.3502956682164733,2.2991726367335303],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=7","opacity":1.0,"showlegend":true,"visible":false,"x":[4.331948131471222],"y":[6.909021517750929],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=8","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[8.344396423199845e-05,7.280309651927916e-05,7.228901458842519e-05,7.987374442755324e-05,9.494004757271294e-05,0.00011727246892313517,0.00014634869665920477,0.00018103799392710988,0.00021983191725560912,0.00026158004831789566,0.0003065134670039248,0.00035729270368977983,0.00041997510279754197,0.0005050421424017779,0.000628705828327605,0.0008142773295054784,0.001092157298118806,0.001496656065615034,0.0020593268636154736,0.0027987120493541055,0.003709320121554739,0.004754563109760982,0.005867270123772528,0.006958423687205954,0.007931975359726976,0.008702280208751962,0.00921075503219505,0.009439009230228073,0.009416249168163538,0.009219072637932136,0.00896218788333195,0.008779433604994575,0.008795285852675198,0.00909206931027279,0.009681028536642619,0.010471220031857149,0.011258498861707994,0.01176594513654034,0.011734880565110531,0.011025456550979975,0.009674378278763891,0.007885072029883543,0.005957524160472964,0.004186942761272318,0.0027728874724081507,0.0017787299960555902,0.0011555266060384534,0.0008043628401386724,0.0006326781488221691,0.0005800606428175846],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=8","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[4.506974582505489,4.490607525140319,4.499777607631226,4.529729818855024,4.574939363619504,4.6298913637683246,4.689708389661365,4.7506110584096195,4.810206338087978,4.867603782957409,4.923362876572384,4.979276719945801,5.038000426605721,5.102538718146161,5.175618018798251,5.258984751196508,5.352715050518732,5.454932809759227,5.5622388873186805,5.6703566991414025,5.774759574966053,5.871225338226678,5.956286791513584,6.027561413070375,6.083952839192781,6.125721675753908,6.154425435922397,6.1727287149732355,6.184086877929664,6.1923112308869745,6.201032235613269,6.213090438779924,6.229908964051747,6.25109085108975,6.274537553471567,6.296748091467201,6.313254640982461,6.319198355211747,6.3099260149541845,6.281588927814267,6.231691229435598,6.1595192380292705,6.0664025788824505,5.955778053224276,5.833045208008271,5.705219284200483,5.58040407833769,5.467124044360185,5.373554670206818,5.306661994851159,3.7038207846869584,3.8955943949798555,4.071609731333412,4.23161035911567,4.376592833949399,4.508796699905358,4.630972260899175,4.745496378082245,4.853685888011787,4.955356957311088,5.048653351522534,5.130152798574965,5.195247166147337,5.2387777620513685,5.255890739605391,5.243014202844184,5.198511300140733,5.122856160401623,5.018528542509786,4.889696834948538,4.741879111035671,4.5814476791780905,4.415048502952732,4.249044766248199,4.0890319918602245,3.939453504642943,3.8033322120292805,3.6821263085525686,3.57571197989455,3.482494132366016,3.3996449338828207,3.3234677370382437,3.249878993190717,3.174991474419773,3.095767445505481,3.0106871519644693,2.920199037110465,2.8264600302086507,2.7326664385349777,2.6423696039003444,2.5588608401365134,2.484666530745739,2.421177512864878,2.3684256504288212,2.3250138644479956,2.2882021565791524,2.2541493682522273,2.2183065785652554,2.175951385324516,2.122841613505034],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=8","opacity":1.0,"showlegend":true,"visible":false,"x":[4.587056987370298],"y":[7.691138525684522],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=9","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.0,8.698554203045079e-25,1.623619298661053e-08,3.655415036244262e-05,0.0007046955338102291,0.003005991896860502,0.0065407876240353895,0.00969221077948311,0.010882066813407244,0.009417186418237307,0.005894494368677824,0.0021651861047840954,0.00024565739729731466,5.890444744258549e-07,2.9901248973241963e-22,9.91328598577342e-226,2.1653566175059905e-12,1.3468101319539288e-05,0.0006941140142214571,0.003476593360402428,0.007529211436883851,0.010714506406092408,0.011603543008693479,0.010001852327719295,0.006755981906155952,0.0032972931229989203,0.0009509971211740053,9.80189147223561e-05,8.090059936560982e-07,1.1803642099358102e-12,8.303559344017288e-42,0.0,1.3708807580926702e-126,1.1169586570300156e-120,5.977425123651932e-101,5.6820728993879995e-50,1.5909709765010299e-15,0.00010921592658045284,0.10247444295293474,0.2752087219296989,0.4196868660646716,0.5129513839109431,0.5286142743028674,0.44038459479225517,0.23103365048522684,0.005299205137663439,2.6316369953722032e-76,8.880101699643955e-70,1.3908658457249528e-145,0.0],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=9","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[2.8551290177121422,3.136857747883641,3.8301290586562646,4.781943004254803,5.81592010343646,6.76621609564118,7.498488325149411,7.921011607436423,7.989542501614188,7.708730821369984,7.131440646509445,6.355686898921646,5.517299762600579,4.775224553476526,4.2860964155886,4.166252450727258,4.445573373622288,5.049536268453369,5.836977314670087,6.64644503479056,7.330527417817886,7.777474696172249,7.922653982933598,7.7528637996871375,7.305613462643527,6.663959239336917,5.946007544549145,5.287343420590473,4.815200954566043,4.61620746925414,4.705979346203553,5.018141541766383,5.436621704133843,5.878508410941112,6.32512021778686,6.7556717259710135,7.158856723183993,7.5329347052310345,7.894711835274651,8.284481427145373,8.681312258582166,8.981867957727015,9.056315462922418,8.818853312824963,8.26335574674558,7.445634916713615,6.428497202522309,5.242181162891001,3.92707004557826,2.623781362340391,2.6141327161210017,3.882771940864619,5.201473652208859,6.418701573855823,7.343961386462325,7.907734705367256,8.179380141121229,8.281364411206729,8.302879414319307,8.261394415477818,8.124122677178057,7.867644283090045,7.523475659570601,7.147698960713569,6.747161205676787,6.316600837678588,5.866063456360887,5.418293487557877,5.008527354313857,4.5991261486107815,4.097091302660224,3.4402473041133947,2.6371508588065105,1.7612820417918935,0.9238988055616368,0.24372526945824635,-0.17782165966104158,-0.2737305351841073,-0.021780802941202992,0.5502092102818308,1.3635174262196945,2.2927530700880423,3.1774303951983365,3.8440721191473384,4.141594466906811,3.989566698136069,3.417877134666237,2.5476172456508737,1.5425726661816226,0.5697295209075421,-0.22697290945702964,-0.7417147648633451,-0.9142200977466053,-0.7327461335970935,-0.23461757747445944,0.49532080686787827,1.3296164384870353,2.1091926919613964,2.663883633573373,2.8454534238731015],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=9","opacity":1.0,"showlegend":true,"visible":false,"x":[5.103586633859458],"y":[8.331261799710944],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=10","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.0,4.6006620049523106e-35,2.2850887388941583e-11,1.2349357972364261e-06,7.240599441974159e-05,0.0005089483652568077,0.00141105615023162,0.0023145890231480444,0.002598063435801204,0.002029017300308247,0.0009931170279281988,0.00021804511519206966,7.565918502783963e-06,4.704157918442892e-10,4.270645369248049e-36,0.0,1.266623058808536e-19,3.699346188138687e-08,2.1230048413631965e-05,0.0002586339413349799,0.0008236527424160322,0.0013609151610708729,0.0014713980180198788,0.0011081524009816162,0.0005574016060328355,0.00015860568235703937,1.693974149928131e-05,2.355318240658295e-07,1.5847571264854433e-11,3.4622866769315605e-24,1.0247307393775345e-94,0.0,0.0,0.0,0.0,5.486808318163093e-256,6.724060148422914e-117,1.843628158197414e-64,7.410564789538639e-15,0.000570854046040476,0.01053658310134061,0.015383865117828523,0.009552364606789949,0.0049345930285780186,4.302953822845676e-05,2.949985119638589e-22,0.0,1.6305352544978261e-220,0.0,0.0],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=10","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[2.8524657468214603,3.12952033035516,3.757487176596706,4.604870467574438,5.521091893815866,6.362093385282682,7.008816238643921,7.379225189895277,7.435011302520133,7.183958553324761,6.678446497786515,6.009915732776687,5.298559944697798,4.677264541062574,4.269173288255161,4.1595494749750275,4.366127748088958,4.829385316832487,5.437902532093004,6.061404143109643,6.5784655486374035,6.8967229701921795,6.965403719498402,6.780734438760591,6.384809611482695,5.858216753838953,5.30652014102836,4.8410041608975956,4.555272514776986,4.501699075009389,4.675221572468226,5.01521586679053,5.435155390544143,5.875888914233714,6.320681202997724,6.754938461808704,7.167489400625382,7.539128079462647,7.851489979449614,8.098202219023278,8.261471551657463,8.333937030974086,8.324996622747447,8.206027234545104,7.890263802808923,7.301502210301452,6.424947905444637,5.295779187195145,3.984102650760243,2.6185082814889697,2.613751054394086,3.9617065736934363,5.277057705326164,6.420187361837482,7.275183654394494,7.838340161485196,8.16927013210076,8.317671998537657,8.319779427866935,8.22371675443919,8.06621280332897,7.841824015390671,7.53450316274306,7.162188259400966,6.750612785223062,6.316337894038885,5.869366826978794,5.424786352592191,5.010460948499867,4.609496671867591,4.160761330946,3.6129137213276064,2.9593948127526937,2.2442286470426875,1.5485167610122077,0.9686942008990309,0.5942900634365995,0.48938199574733465,0.6794927747831143,1.1444537630572724,1.817444166819254,2.5906033583859593,3.327903196089125,3.885956954264269,4.142725231001319,4.03212172152882,3.5708285747766717,2.8476426586692103,1.991920245115633,1.1440847346678336,0.4323256181530808,-0.04398810093927841,-0.22490617844648764,-0.09556862394520227,0.3122501855266169,0.9225003566715886,1.6215462718829794,2.270129776833955,2.721695658901528,2.84769580253708],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=10","opacity":1.0,"showlegend":true,"visible":false,"x":[4.993654014104051],"y":[8.348254087751911],"type":"scatter"}],                        {"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}},"xaxis":{"anchor":"y","domain":[0.0,0.98],"matches":"x2","showticklabels":false,"range":[-1,7],"title":{"text":"X"}},"yaxis":{"anchor":"x","domain":[0.575,1.0]},"xaxis2":{"anchor":"y2","domain":[0.0,0.98],"range":[-1,7]},"yaxis2":{"anchor":"x2","domain":[0.0,0.425]},"annotations":[{"font":{"size":16},"showarrow":false,"text":"Surrogate","textangle":90,"x":0.98,"xanchor":"left","xref":"paper","y":0.7875,"yanchor":"middle","yref":"paper"},{"font":{"size":16},"showarrow":false,"text":"Acquisition","textangle":90,"x":0.98,"xanchor":"left","xref":"paper","y":0.2125,"yanchor":"middle","yref":"paper"}],"title":{"text":"Gold Search"},"sliders":[{"active":0,"steps":[{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"0"}],"label":"i = 0","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"4"}],"label":"i = 1","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"7"}],"label":"i = 2","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false],"title":"10"}],"label":"i = 3","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,true,true,true,false,false,false,false,false,false,false,false,false],"title":"13"}],"label":"i = 4","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,false,false,true,true,true,true,false,false,false,false,false,false],"title":"16"}],"label":"i = 5","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,false,false,true,false,false,true,true,true,true,false,false,false],"title":"19"}],"label":"i = 6","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,false,false,true,false,false,true,false,false,true,true,true,true],"title":"22"}],"label":"i = 7","method":"update"}]}]},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>

### Upper Confidence Bound (UCB)

Choose the next point by trading off between surrogate's posterior mean and uncertainty.

$$
\begin{align*}
x_{t+1} = \arg\max_x \mu_t(x) + \sqrt{\beta} \sigma_t(x)
\end{align*}
$$

In [47]:
generation_strategy = create_generation_strategy(
    botorch_acqf_class=UpperConfidenceBound
)
ax_client = create_client(generation_strategy=generation_strategy)
predictions, acquisitions = run_ax(n=10, ax_client=ax_client)
results["UCB"] = ax_client.get_trials_data_frame()

[WARNING 08-11 10:42:41] ax.service.ax_client: Random seed set to 1. Note that this setting only affects the Sobol quasi-random generator and BoTorch-powered Bayesian optimization models. For the latter models, setting random seed to the same number for two optimizations will make the generated trials similar, but not exactly the same, and over time the trials will diverge more.
[INFO 08-11 10:42:41] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[RangeParameter(name='x', parameter_type=FLOAT, range=[0.0, 6.0])], parameter_constraints=[]).
[WARNING 08-11 10:42:43] ax.service.utils.report_utils: Column reason missing for all trials. Not appending column.


In [48]:
render_plotly_html(
    plot_surrogate_and_acquisition(
        x=x,
        y=y,
        ax_client=ax_client,
        gold_fn=gold,
        predictions=predictions,
        acquisitions=acquisitions,
        line_kwargs=get_line_kwargs(),
    )
)

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="7f2540bf-9160-45ed-baf1-d58be44eec3b" class="plotly-graph-div" style="height:100%; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("7f2540bf-9160-45ed-baf1-d58be44eec3b")) {                    Plotly.newPlot(                        "7f2540bf-9160-45ed-baf1-d58be44eec3b",                        [{"hoverinfo":"skip","mode":"lines","name":"Ground Truth (f)","showlegend":true,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[2.85,3.856123347536194,4.638417508253971,5.221510704359092,5.628898102467025,5.8829418136029314,6.00487089320169,6.01478134110787,5.9316361015757515,5.773265063269314,5.5563650592622364,5.296499867037907,5.008100208489416,4.7044637499195545,4.397755102040818,4.099005819975396,3.818114403255205,3.5638462958218278,3.343833886026604,3.1645765066304996,3.0314404348042556,2.948658892128277,2.919332044592691,2.9454270025973184,3.0277778209516644,3.166085498874992,3.3589179799961926,3.6037101523539157,3.896763848396514,4.233247844982003,4.607197863378097,5.011516569262348,5.4379735727217735,5.877205428253326,6.318715634763429,6.7508746355685645,7.1609198183944756,7.534955515376893,7.857953003061169,8.113750502402425,8.28505317876541,8.35343314192454,8.29932944606415,8.10204808977798,7.739762016069648,7.18951111235242,6.427202210449309,5.42760908659298,4.164372461425842,2.6100000000000705],"type":"scatter","xaxis":"x","yaxis":"y"},{"marker":{"size":10},"mode":"markers","name":"i=1","opacity":1.0,"showlegend":true,"visible":true,"x":[1.8140525221824646],"y":[4.153277647970732],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=2","opacity":1.0,"showlegend":true,"visible":true,"x":[5.636016067117453],"y":[6.4030358079544385],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=3","opacity":1.0,"showlegend":true,"visible":true,"x":[4.097510201856494],"y":[6.082020053347733],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=4","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.5385537455963063,-0.586919132471347,-0.6353555829071795,-0.6834275172359378,-0.7306248079001517,-0.7763541519346802,-0.8199287658387051,-0.8605552153030349,-0.897315243803269,-0.9291389589480386,-0.9547638702576812,-0.9726741465483395,-0.9810253962753392,-0.9776108885815831,-0.9600583667768401,-0.9265613037683571,-0.8770132383870983,-0.8133804260585877,-0.7387206493432023,-0.6560692544643613,-0.5679836547461643,-0.4765359212254989,-0.3834248644437226,-0.2900741243979332,-0.19769333173470782,-0.10730902652184487,-0.019774021337617576,0.06423938655426303,0.14425954945891076,0.22004624022986016,0.2916244349646481,0.3592985766156801,0.42359611088465926,0.4850656492096811,0.5439126580066164,0.5996628156545168,0.6512023207783356,0.6971815842352724,0.7364206221845143,0.7681279177031611,0.791968029180581,0.8080734775267988,0.8170640008159974,0.8200909417511887,0.8188691337476174,0.8155700173953773,0.8123905876617088,0.8108293232923862,0.8112170583316103,0.8129835691100369],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=4","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[5.879828741772096,5.723684944424338,5.564919034717484,5.405287615415519,5.246875209974377,5.092092146564724,4.943655173439945,4.804546034740408,4.677943045572257,4.567120898175266,4.4753146866562545,4.405545664614189,4.360408768005911,4.341825638785639,4.350771871227595,4.386993354512391,4.448748389221656,4.532810844813912,4.634893013277516,4.750143492373074,4.873588620047045,5.000504620600418,5.12671443494951,5.248806696645397,5.364276715061822,5.471590800773641,5.570176158374724,5.660339316717575,5.74311715203231,5.820066490320642,5.893001544577461,5.96369348171465,6.03355350613943,6.103329968324751,6.172860705100469,6.24095696127736,6.305593589211606,6.364345953453986,6.4148589511706895,6.45527159344706,6.484555617589533,6.502739129116825,6.51099724395559,6.511601248774515,6.50772643883592,6.503127171113509,6.501696264117567,6.50693847950454,6.521501446900843,6.547022552377477,6.101743942952618,6.170066285289676,6.219591383202151,6.250977680328067,6.2659653602492105,6.267250979972175,6.257994311081833,6.241256977277889,6.219539143177324,6.194444308974291,6.166489252021625,6.135068025432309,6.098571020386865,6.054651956833938,6.000626656609064,5.933977068904017,5.852922089199586,5.75696588950724,5.647101205867781,5.525598774378168,5.395669412032708,5.2610911299200485,5.125838350762745,4.993740002771914,4.868184535225848,4.751883097110591,4.646697269002982,4.553534562066633,4.472312966795951,4.401994655091324,4.340688005214141,4.285815939106026,4.234346690290113,4.183080205450835,4.128979247612083,4.069527932593617,4.003040362354105,3.928733988138434,3.8466290758021366,3.757397508226621,3.662195051125944,3.5624967627493516,3.4599483111916736,3.356240325414143,3.2530086498943227,3.1517603858862326,3.053823678413531,2.960318116876881,2.872142141022751,2.789973795802151],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=4","opacity":1.0,"showlegend":true,"visible":false,"x":[5.28214746108094],"y":[8.062511138469858],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=5","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.3645544599693048,-0.40620889697438295,-0.4487693572292339,-0.49192446251275784,-0.5352867931952072,-0.5783809667447924,-0.6206302365267578,-0.6613417172991769,-0.6996908783446095,-0.734707209821059,-0.7652656554245167,-0.790093446698328,-0.8078097463659468,-0.8170232570448337,-0.8165106445340357,-0.805470278608273,-0.7837843463918496,-0.7521019716974495,-0.7116312674951332,-0.6638439501296887,-0.610234563847381,-0.5521738522199584,-0.4908427898560223,-0.42721627164676834,-0.3620706508665546,-0.29599995394036943,-0.22943391205926533,-0.16265600006365405,-0.09582268167457597,-0.028987258501393776,0.03786622588228028,0.10477179492431296,0.17170559767877988,0.2384816417742628,0.30462628455505275,0.3692708242365497,0.43118429861835716,0.48894474321941783,0.5411367947973023,0.5865383405029793,0.6242835810080976,0.6539958781882218,0.6758757202486636,0.6907123257587958,0.6997878473159334,0.7046478498566683,0.7067206022031154,0.7069921589392384,0.7059138541771491,0.7035878155004716],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=5","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[8.089770783263793,7.860703606414598,7.622117300893126,7.376099688338648,7.1253219785175155,6.873069748980079,6.623248354985064,6.380352899230695,6.149391768108006,5.935752228225059,5.744997078470032,5.58258337413377,5.453498361348393,5.361814567530566,5.310175925435652,5.299239875807018,5.327143502321956,5.38943477851384,5.479778491746931,5.59080935235496,5.714888049790666,5.84473582507414,5.973937716933844,6.0973122090921255,6.211149692918072,6.313324411622921,6.4032851704564395,6.4819300423332695,6.5513705965315605,6.614592876266389,6.675026473408285,6.73604051585881,6.800396840039718,6.86970610537781,6.943951357454329,7.02123206846183,7.098170925213172,7.170833401164502,7.235622256157267,7.289998308777529,7.332970781549623,7.365330749429897,7.38962938420428,7.409928660757309,7.431374597500959,7.459632097178986,7.500162634007157,7.557375773358315,7.633914594137186,7.730588830641307,6.057821125822733,6.230772420779854,6.371089301576157,6.476336139352336,6.545461224194559,6.5788961681584315,6.57849542239355,6.547538323694363,6.490510558127817,6.412296036017706,6.317348203152218,6.209111962187286,6.089735703082352,5.960086505855439,5.820057379900498,5.669128591613826,5.507115907422042,5.334960267867072,5.155100335004108,4.971280644884314,4.788145989892904,4.610759434375058,4.444109019682951,4.2926493069475855,4.159908160836719,4.048177439531344,3.9582984796420484,3.8895487960916713,3.839634325606318,3.804790792464836,3.779997306493481,3.7593040739037846,3.7362731330785035,3.704525497667028,3.6583795253964198,3.593550986385698,3.507730674810319,3.4005898048328476,3.2734146272854217,3.128687205120473,2.96967844483979,2.800084369444627,2.62372251482942,2.444294529204493,2.265213518386304,2.0894899480624605,1.9196673836692617,1.7577984227955428,1.6054513354061761,1.4637387576621972],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=5","opacity":1.0,"showlegend":true,"visible":false,"x":[5.715464231391885],"y":[5.7787487222264815],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=6","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.4134886197966897,-0.45455734654670155,-0.4968745571657266,-0.5401341389664015,-0.5839413156600692,-0.6277971917928746,-0.6710813125660736,-0.7130323705440398,-0.7527278176722061,-0.7890646165350805,-0.8207465138281738,-0.8462891956131811,-0.864064098433035,-0.8724115757131474,-0.8698529598639331,-0.8553993566887226,-0.8288810588370025,-0.7910574138038355,-0.7433578973910886,-0.6875235595871645,-0.6253226531389444,-0.5583809485831153,-0.48810694968801366,-0.41567444135838544,-0.3420322054535073,-0.2679233950974983,-0.19390662722791885,-0.12037664009079979,-0.04758592027585479,0.02432848576723784,0.09530589138793927,0.16530080996971824,0.2341891420803035,0.3016361380649871,0.36693535502046004,0.42887065774623934,0.48575744727800374,0.5356591951261093,0.5766346679482592,0.6069706907311291,0.6253949414097821,0.6312802383864801,0.6248503638174534,0.6073709745403796,0.5812554232376044,0.5498735910367925,0.5167823601568517,0.48477712556070046,0.45534888090941783,0.4288731299785815],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=6","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[7.576300754476621,7.399635932766348,7.212976444204291,7.017743821689516,6.815917149801075,6.610092318577717,6.403521627786201,6.200122507013764,6.004441928939392,5.821561341955104,5.65692614511161,5.516084567874959,5.404324170014147,5.326201019632968,5.28496783320163,5.281923380666701,5.315757910066951,5.382409802064481,5.475806973348677,5.588773054151802,5.71381771963976,5.8437874049713905,5.972370993502309,6.094464072793638,6.206399984830421,6.306056958048309,6.392849286957459,6.467608136148658,6.532355443601211,6.589973965377437,6.64377915101628,6.697005657735562,6.752234098102101,6.810802656912812,6.872273114200918,6.934126560972997,6.9921956865557755,7.041671805235057,7.0780864956820935,7.098109589986862,7.100111119604184,7.08446953324168,7.053639856567529,7.01202396419479,6.965707464856334,6.922033247018113,6.88875903062333,6.872863262483258,6.879288417619,6.9104013765599435,5.822273132560526,5.9912315208525335,6.131473200357386,6.240537467006419,6.317258108938576,6.361776532783678,6.375464578991521,6.3610345630503895,6.32246307670857,6.264189492797135,6.190245233462045,6.1036398985259215,6.006050309329502,5.897830956053315,5.7783394126480125,5.646541724892816,5.50183021782603,5.344893706028416,5.1781085967511755,5.00528892320304,4.831217004282355,4.661114692425046,4.50012438754282,4.352844083976038,4.222941523406904,4.112859521836505,4.023617129870907,3.9547082672096545,3.904099440399525,3.8683296805528062,3.842717522904155,3.821680313818009,3.79916902737602,3.7692158792300603,3.726581493635981,3.6674700149148265,3.5901078610879296,3.494695390876932,3.3829653801445367,3.2577041046273383,3.122308549513858,2.980410819165079,2.835583172753023,2.6911245397058647,2.549921416427718,2.41437178001636,2.2863590659595414,2.1672634466752116,2.0579988983109385,1.959066323815064],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=6","opacity":1.0,"showlegend":true,"visible":false,"x":[5.0165540567741385],"y":[8.353042361423036],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=7","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.36274088699771156,-0.3881799851477882,-0.4184122481783814,-0.45422181423564867,-0.49645855090730473,-0.5460132397436911,-0.6037764910343892,-0.6705765353418018,-0.7470905966398264,-0.8337244806212194,-0.9304554217959884,-1.0366335043447155,-1.1507316383837898,-1.2699792663108902,-1.3891004041680317,-1.454132961531623,-1.353286213510054,-1.2415720782684567,-1.1338134954298575,-1.033908370931564,-0.9440423343477122,-0.8653142950192151,-0.7979970859129981,-0.7417107382123834,-0.6955344459615816,-0.6580597598771463,-0.6273865917172258,-0.601065928089213,-0.5759966676744728,-0.5482889678365598,-0.5131119229335825,-0.46453606231792366,-0.395233462386914,-0.29320312928481157,-0.08414411934622121,0.19984122837017676,0.47523647866274965,0.7245636440531938,0.935018864971134,1.0958779325158234,1.199065308195765,1.2424110037996832,1.2148695291645935,1.0737436330425894,0.8121193129701074,0.43121331247149314,-0.045370321918906026,-0.5257505253715541,-0.9316041302614675,-1.2511332278229312],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=7","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[12.56345373133549,12.35626091083674,12.093520159625392,11.764123007086429,11.356736043566272,10.86096607367824,10.269131261165466,9.578728728478108,8.795586756999981,7.937489832493709,7.037734057286789,6.147593199980982,5.336087492708497,4.684890050715658,4.275996588296173,4.170453723850872,4.380007698977817,4.855326550110301,5.509292197208063,6.243762579055863,6.967345472614708,7.604862399730535,8.100828866082617,8.419479978921196,8.543425584797543,8.472342389867212,8.222408316783635,7.826514337123495,7.33463696214579,6.813106297987871,6.340920150204285,6.000955423372265,5.864391133742632,5.968660468586983,6.293701019272335,6.752450228523464,7.227830689813137,7.630573040959817,7.928507849296807,8.138147399184959,8.28677634751282,8.367861745803182,8.326563745509945,8.106692260901758,7.695648880240936,7.102626938994457,6.371377777239635,5.613624812565279,4.983736200654257,4.600415600136827,3.940189100944672,4.775688640562266,5.579887195518154,6.357633468155488,7.072585924044096,7.6677365529465416,8.087014175299975,8.3076607340964,8.346495331798138,8.209825254091875,7.912985551767977,7.516836663468899,7.109909392365481,6.762382259103688,6.487531361672997,6.232682892297781,5.907184283416737,5.438145789736037,4.808357097308292,4.050988145136694,3.2291859776210066,2.416199017527731,1.6811690496537266,1.081174039026556,0.6580222555193802,0.43777758154640534,0.4312532808141243,0.6342649682915309,1.0270579771825696,1.5729566517207059,2.2169348419995436,2.8854897586387382,3.489854990942269,3.9350036077496533,4.136649144780818,4.046764110383214,3.6756499421015296,3.0807503165414047,2.3395987403161214,1.529372396419225,0.7150116839175418,-0.05566324187737681,-0.7521209875874355,-1.358676035663219,-1.8710020733806534,-2.2925956490458814,-2.6317169583276376,-2.899010475823361,-3.105812581667477,-3.2630537702004165],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=7","opacity":1.0,"showlegend":true,"visible":false,"x":[5.045794885225497],"y":[8.352948194884533],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=8","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.6360814102529371,-0.6525555475115393,-0.6729752157076666,-0.6981418854263717,-0.7289552720837588,-0.766399125890082,-0.8115134558287226,-0.8653486162066143,-0.9288959318384364,-1.0029889360190651,-1.0881690576420027,-1.1845100419743242,-1.2913968808936265,-1.4072571498729758,-1.5292318880899427,-1.6077938448838565,-1.49058046523736,-1.3790684696619881,-1.2770090789025101,-1.1864436950365274,-1.1082833346326577,-1.0425627335838519,-0.9886363752461993,-0.9453172794618773,-0.9109586605428512,-0.8834814220250699,-0.8603530740722093,-0.8385265807439963,-0.8143519432742058,-0.7834804048151537,-0.7407929409582855,-0.6804037473411751,-0.5958168409613929,-0.4802747530096896,-0.24964146805436765,0.052410802234749754,0.33372487914019877,0.5794751109485696,0.7775980699032167,0.9194499434201546,1.0002499013587423,1.019717289036653,0.9889724474923199,0.8618736154502842,0.6519947297174815,0.307953477842337,-0.19541907217864654,-0.797587158782355,-1.3834070141344537,-1.8878524812419435],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=8","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[14.899487098845947,14.59731824625456,14.219299303029757,13.752573302449534,13.184908973420045,12.50629333222417,11.711155560461776,10.801245388207903,9.789054259773252,8.701440274025298,7.582779828056482,6.496525298267478,5.523557081900988,4.755332914857103,4.279850256945082,4.159288377387758,4.401687111531412,4.949738428555891,5.704339242251746,6.552252234819074,7.385596009375586,8.113398437382568,8.667095180999294,9.002207970879372,9.098139325732944,8.957422472041884,8.605068993439598,8.08795015561714,7.4734659139563195,6.846145746387824,6.300416096830881,5.927840723195359,5.798178219339359,5.93625889353408,6.30148458813715,6.787046172700685,7.267471551058512,7.659951544891383,7.946252560064422,8.150426982512341,8.29220366903258,8.353690466491,8.296126679967244,8.101448379150634,7.75771517139026,7.210870616330006,6.423709561752764,5.46159286000988,4.4992454043535,3.7173729849391735,3.4363744798695195,4.448386089366773,5.459534061882181,6.4231928485077265,7.2065143041822495,7.753768893192425,8.100878037864577,8.293719029346061,8.353364606224746,8.269792707957093,8.03352553758157,7.673142112342545,7.262181253093345,6.879546555345489,6.558681308408256,6.261994347928036,5.89942624182173,5.386156493646027,4.690416252141956,3.837041100903333,2.8905934909793167,1.9346816090369696,1.0546214210789047,0.325696758424332,-0.193456140144602,-0.46390309769677973,-0.46757853228987933,-0.20785561994798218,0.28977780687320775,0.9769024424246795,1.7818699546774024,2.611372446976623,3.355817515431063,3.9007390033472946,4.146114545225724,4.033807505948925,3.570915495805598,2.81858575469758,1.863813383412925,0.7971554325291041,-0.30127334576935905,-1.3686421198749938,-2.3610573960803016,-3.2520187545426635,-4.0292842902159745,-4.69126371249193,-5.243614544617011,-5.696379529279881,-6.0617765403625725,-6.352617664133875],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=8","opacity":1.0,"showlegend":true,"visible":false,"x":[4.9993789174230505],"y":[8.349843198387447],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=9","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.796464324431568,-0.8121960086675974,-0.8318440902939169,-0.8561997518668545,-0.8861462728038825,-0.9226443155428149,-0.9667045364759566,-1.0193434292555343,-1.081517637643299,-1.154031414063758,-1.2374116104070108,-1.331744801912472,-1.4364720753084201,-1.5501380295854703,-1.6700777482577924,-1.7476382208868741,-1.6328984019018842,-1.5245444345197972,-1.4259975718809406,-1.3390442774742342,-1.2644037136188453,-1.2019612849805137,-1.1509443161970534,-1.1100438363122145,-1.0774842182643856,-1.0510445513735878,-1.0280379753978766,-1.0052580983039348,-0.9789059504970099,-0.9445179227124105,-0.8969264908469698,-0.8303034812669818,-0.7383606065495942,-0.6147336095956321,-0.3810172689731264,-0.0808528632588304,0.19842830063232972,0.44275086612839026,0.6409165875123386,0.7851381746784056,0.8711503538410656,0.898399340492169,0.8673460751281438,0.7404519246779215,0.5276293663742984,0.18085468117389628,-0.32472969151527276,-0.9314305584665407,-1.527875864420319,-2.0494747045627135],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=9","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[15.131163680845056,14.793425971981248,14.376228559970052,13.867659639665115,13.25695982290163,12.536144483045446,11.702174733262288,10.759658820866607,9.723933856755961,8.62416960777616,7.505842242835078,6.43155966647697,5.4788401499898,4.73318763685476,4.274911568255967,4.158949202708486,4.389962841629986,4.912797605312843,5.6334829821189345,6.44411969641588,7.2409310446980815,7.935510370006517,8.460715911296433,8.77302086885251,8.852923219512984,8.704533141916055,8.354858349973975,7.852688601300532,7.2663925750092595,6.679451080333329,6.182298089301333,5.859284910115759,5.770730128871854,5.932556859478343,6.300215400515167,6.771989855237504,7.23476122306415,7.618238152631982,7.910024196300097,8.129948381049752,8.286473817404215,8.353497617725283,8.296166782154828,8.101615778557067,7.756560007201858,7.20918082543622,6.4233917716398725,5.461225268407107,4.489480636557436,3.6809727051443843,3.4229645130906388,4.442762796454438,5.459252603272109,6.422885242441785,7.205320189774224,7.753156049852195,8.101082792601348,8.294393836153073,8.353328471826304,8.275020540858932,8.054811417725952,7.712554109384889,7.309440788545064,6.919055952180956,6.57981430303293,6.266106114804881,5.9000988282887565,5.402474429925359,4.738372081616255,3.924727437626209,3.0176111380568953,2.094204230553497,1.2364111556806119,0.5188374579889987,0.0012595765124698843,-0.275478503905064,-0.29148427898111073,-0.048866168092808415,0.4275430549277548,1.0897202038644433,1.8667839055917224,2.667256810226082,3.384871390796116,3.9097329495178834,4.146294635499876,4.038178248384177,3.5891183747524043,2.853363950977284,1.9107244119071365,0.8463501805152678,-0.26248123937455947,-1.353316955618995,-2.380771498571095,-3.315718380548933,-4.142829545361105,-4.8574817873661384,-5.462682841663506,-5.966375905939984,-6.379273074715096,-6.713236228633146],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=9","opacity":1.0,"showlegend":true,"visible":false,"x":[5.038983862056284],"y":[8.353604872575431],"type":"scatter"},{"hoverinfo":"skip","mode":"lines","name":"a=10","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.9202538824104529,-0.9361281076901904,-0.9559634328765323,-0.9805597387881465,-1.010809715070308,-1.0476839337978432,-1.092203141538557,-1.145393652830414,-1.208221053755085,-1.2814968588364621,-1.3657524694714844,-1.4610749891882888,-1.5669003712907343,-1.6817603835111794,-1.8029672159873853,-1.8813452868152323,-1.7653206911216284,-1.6557916751126793,-1.5561933687014187,-1.4683172131062157,-1.3928775108758797,-1.3297463276751715,-1.278130026265389,-1.2366914502324664,-1.2036195881149088,-1.1766506881862933,-1.1530471690628563,-1.129543608504193,-1.102273492532014,-1.0666975071812943,-1.017565672478554,-0.948963818813985,-0.8545202948424676,-0.7278015013410749,-0.49004459421484614,-0.18548331741287727,0.09799910025020273,0.3462436492169475,0.5480190764337439,0.6955399691521506,0.7845139501525253,0.8132552198705765,0.7813180391613506,0.6526007906376129,0.4356672010744566,0.08260531918789378,-0.43211500836373296,-1.0502361148624217,-1.6585833566111916,-2.191261666771573],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=10","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[15.010767877655201,14.675115076385527,14.26077834775662,13.756045613569139,13.150371176904452,12.435979307628633,11.610005334987935,10.677154208962277,9.652726469043914,8.565656947610911,7.460923553017993,6.400325535506802,5.460260747183061,4.724882263033541,4.273122131022453,4.158868138751297,4.386534341062323,4.901720795965945,5.611839318521209,6.41056524233714,7.195601120113388,7.879774482007088,8.396882583662189,8.704048843428335,8.782158749002221,8.635467133252204,8.29088288555173,7.796829869582867,7.2210069212029335,6.645893775601972,6.160610996087088,5.847996638583442,5.766909544525106,5.932282199727337,6.299570121339346,6.768434030660749,7.2280525628632875,7.610213384891543,7.903331062386096,8.126312714444,8.285562899872508,8.353562555737353,8.296229247464236,8.101623100930786,7.75641050428671,7.209134351406138,6.423462285229208,5.460969322899211,4.487851176940622,3.675858028389271,3.4229308351597676,4.442169939339741,5.459057064726086,6.422973820877711,7.205401068959955,7.75314361753708,8.101115454012925,8.29475131622086,8.353435689998593,8.275181805060276,8.056803456565278,7.717114370233848,7.315334159003698,6.924044891637993,6.582307825555239,6.266402555053479,5.900628718889338,5.406950271345,4.750495231964813,3.9472388051799028,3.0518428498734016,2.1400312191145203,1.292447063293769,0.5827382684478182,0.07004402123401832,-0.20513638722885652,-0.22299918082243764,0.014491578873689903,0.4828808456903464,1.1347774053167536,1.9002133820688476,2.688914342108518,3.3960571340947894,3.913286379899034,4.146406740047306,4.0397759646283165,3.596880181245991,2.870933950499743,1.9403920150868181,0.8890790107696467,-0.20682366238564764,-1.28564996066528,-2.3024941994604404,-3.228449913894181,-4.048214149110743,-4.757058647279818,-5.357811282566192,-5.858202971961673,-6.268730563917068,-6.6010560913442085],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=10","opacity":1.0,"showlegend":true,"visible":false,"x":[5.035939505891532],"y":[8.353772660864934],"type":"scatter"}],                        {"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}},"xaxis":{"anchor":"y","domain":[0.0,0.98],"matches":"x2","showticklabels":false,"range":[-1,7],"title":{"text":"X"}},"yaxis":{"anchor":"x","domain":[0.575,1.0]},"xaxis2":{"anchor":"y2","domain":[0.0,0.98],"range":[-1,7]},"yaxis2":{"anchor":"x2","domain":[0.0,0.425]},"annotations":[{"font":{"size":16},"showarrow":false,"text":"Surrogate","textangle":90,"x":0.98,"xanchor":"left","xref":"paper","y":0.7875,"yanchor":"middle","yref":"paper"},{"font":{"size":16},"showarrow":false,"text":"Acquisition","textangle":90,"x":0.98,"xanchor":"left","xref":"paper","y":0.2125,"yanchor":"middle","yref":"paper"}],"title":{"text":"Gold Search"},"sliders":[{"active":0,"steps":[{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"0"}],"label":"i = 0","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"4"}],"label":"i = 1","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"7"}],"label":"i = 2","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false],"title":"10"}],"label":"i = 3","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,true,true,true,false,false,false,false,false,false,false,false,false],"title":"13"}],"label":"i = 4","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,false,false,true,true,true,true,false,false,false,false,false,false],"title":"16"}],"label":"i = 5","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,false,false,true,false,false,true,true,true,true,false,false,false],"title":"19"}],"label":"i = 6","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,true,false,false,true,false,false,true,false,false,true,false,false,true,false,false,true,true,true,true],"title":"22"}],"label":"i = 7","method":"update"}]}]},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>

### Thompson Sampling
Choose the next point by sampling from the surrogate's posterior (or a sum over a batch of samples) and then optimizing along this trajectory.

In [49]:
generation_strategy = create_generation_strategy(
    botorch_acqf_class=PathwiseThompsonSampling
)
ax_client = create_client(generation_strategy=generation_strategy)
predictions, acquisitions = run_ax(n=10, ax_client=ax_client, acqf_n=5)
results["Thompson"] = ax_client.get_trials_data_frame()

[WARNING 08-11 10:42:43] ax.service.ax_client: Random seed set to 1. Note that this setting only affects the Sobol quasi-random generator and BoTorch-powered Bayesian optimization models. For the latter models, setting random seed to the same number for two optimizations will make the generated trials similar, but not exactly the same, and over time the trials will diverge more.
[INFO 08-11 10:42:43] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[RangeParameter(name='x', parameter_type=FLOAT, range=[0.0, 6.0])], parameter_constraints=[]).
[WARNING 08-11 10:42:45] ax.service.utils.report_utils: Column reason missing for all trials. Not appending column.


In [50]:
render_plotly_html(
    plot_surrogate_and_acquisition(
        x=x,
        y=y,
        ax_client=ax_client,
        gold_fn=gold,
        predictions=predictions,
        acquisitions=acquisitions,
        line_kwargs=get_line_kwargs(color="red"),
    )
)

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="7672e290-06ad-4114-af5a-1086351874e2" class="plotly-graph-div" style="height:100%; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("7672e290-06ad-4114-af5a-1086351874e2")) {                    Plotly.newPlot(                        "7672e290-06ad-4114-af5a-1086351874e2",                        [{"hoverinfo":"skip","mode":"lines","name":"Ground Truth (f)","showlegend":true,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[2.85,3.856123347536194,4.638417508253971,5.221510704359092,5.628898102467025,5.8829418136029314,6.00487089320169,6.01478134110787,5.9316361015757515,5.773265063269314,5.5563650592622364,5.296499867037907,5.008100208489416,4.7044637499195545,4.397755102040818,4.099005819975396,3.818114403255205,3.5638462958218278,3.343833886026604,3.1645765066304996,3.0314404348042556,2.948658892128277,2.919332044592691,2.9454270025973184,3.0277778209516644,3.166085498874992,3.3589179799961926,3.6037101523539157,3.896763848396514,4.233247844982003,4.607197863378097,5.011516569262348,5.4379735727217735,5.877205428253326,6.318715634763429,6.7508746355685645,7.1609198183944756,7.534955515376893,7.857953003061169,8.113750502402425,8.28505317876541,8.35343314192454,8.29932944606415,8.10204808977798,7.739762016069648,7.18951111235242,6.427202210449309,5.42760908659298,4.164372461425842,2.6100000000000705],"type":"scatter","xaxis":"x","yaxis":"y"},{"marker":{"size":10},"mode":"markers","name":"i=1","opacity":1.0,"showlegend":true,"visible":true,"x":[1.8140525221824646],"y":[4.153277647970732],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=2","opacity":1.0,"showlegend":true,"visible":true,"x":[5.636016067117453],"y":[6.4030358079544385],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=3","opacity":1.0,"showlegend":true,"visible":true,"x":[4.097510201856494],"y":[6.082020053347733],"type":"scatter"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=4","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-1.5143374053402645,-1.4768356097546933,-1.4318596212352939,-1.3789017463980668,-1.3179185868305199,-1.2493493979274055,-1.1741084101268393,-1.0935490969054198,-1.0093998105016146,-0.9236718715242969,-0.8385429797943615,-0.7562205697982192,-0.6787913052983159,-0.6080641284449819,-0.5454149922459561,-0.4916414781108611,-0.4468372957028972,-0.4103281444906126,-0.38070416269326435,-0.3559052380678631,-0.33334376596836446,-0.31006354566435546,-0.28293020339325015,-0.2488450440935308,-0.2049711897075892,-0.14895849313068155,-0.07915221924277205,0.005230001851128208,0.10396785014636789,0.21576785813916288,0.3382634260880151,0.4680924933078776,0.6010560902165198,0.7323568134421228,0.8569121051354021,0.9697145289890516,1.06611981619812,1.1420521631191707,1.1942056950364734,1.2202336271755156,1.218903624812584,1.1902012131114474,1.1353675667703715,1.0568633159568865,0.9582558069160505,0.8440331689723102,0.719354156627247,0.589747896847939,0.46078789844391643,0.3377723484090247],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=4","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.7171138940674793,-0.7874537197488348,-0.8556275417116243,-0.9201310455539913,-0.9795808393559312,-1.032759746162619,-1.0786452484094942,-1.1164212254932568,-1.1454746274368015,-1.1653799793658464,-1.175875504352168,-1.176835112648739,-1.1682405017521296,-1.1501571564641386,-1.1227171859254996,-1.0861107769472165,-1.0405869004248482,-0.9864652084278054,-0.924159423287466,-0.8542052083181987,-0.7772873485998674,-0.6942621771539549,-0.6061713116068338,-0.5142433007095832,-0.41988069906182424,-0.3246313031877306,-0.23014367365473687,-0.1381084977016389,-0.05018866952720691,0.032057957873719456,0.10725848429772933,0.1743026161771788,0.23241339127416927,0.281207066084707,0.32073946565163514,0.351531744351417,0.37454264289598305,0.3910909798089046,0.40276230331222496,0.41130778691022996,0.41854014868098943,0.4262323558805159,0.4360253494211537,0.44935095033492056,0.4673755175982911,0.49096888386817406,0.5207017126301674,0.5568722801043402,0.5995473330594946,0.6485882431394288],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=4","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-2.0433418462973156,-2.0162354916667216,-1.9645361616667392,-1.890504688417991,-1.7980321063366382,-1.69235971567972,-1.5795581425651188,-1.4658417774485721,-1.3568288133313877,-1.2568705676717595,-1.1685640871538434,-1.09253104448091,-1.027499735435087,-0.9706746979423697,-0.9183304266449428,-0.8665312955523659,-0.8118594798099819,-0.7519568777186432,-0.6857273222469689,-0.6132857364338637,-0.5357094471775532,-0.454646651410177,-0.37186780597484437,-0.2888576281777737,-0.2065354381366602,-0.1251622281013871,-0.04445058205662766,0.03615248621640532,0.11707967208144043,0.19824965889948998,0.2787657261794727,0.35679033015747774,0.4296443518604576,0.4941333974064641,0.5470553220618931,0.5857994572145417,0.6089077754514857,0.616487161624968,0.6103995286989371,0.5941793045264788,0.5726755487607295,0.5514678749326187,0.5361484232350026,0.5315878785076957,0.5413069137496964,0.567054859656658,0.6086588086368039,0.6641563808532082,0.7301718844552028,0.8024512096593114],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=4","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-2.370567133657792,-2.452800522946071,-2.527570938982053,-2.5892844443194125,-2.6326456416812496,-2.653038297269549,-2.646863132796219,-2.61180742912543,-2.5470261217435652,-2.4532208060425074,-2.332611059031491,-2.188801180188893,-2.0265542599184663,-1.8514937911315565,-1.6697602741297493,-1.4876559307755608,-1.3113079346277658,-1.1462960628890535,-0.9972004808359345,-0.867221101492228,-0.7579320744936701,-0.6691816755139839,-0.5991386726850482,-0.544477401498621,-0.5006849613618539,-0.46246581155562994,-0.4242121943184354,-0.3805037535243898,-0.32659682027916226,-0.2588633112865344,-0.17514106333617452,-0.07496155673691973,0.04037296250427813,0.1678834443931294,0.3031909804674553,0.4409391208483733,0.5751258697677857,0.6993393392284468,0.8070783053072136,0.8921462833115421,0.9490738444635574,0.9735247875775842,0.962645128921586,0.9153194047752962,0.8323061494823426,0.7162331249225709,0.5714423315623894,0.4036865371823616,0.21974562234276787,0.02708537278563658],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=4","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.06232746882425144,0.0011519325080755483,-0.07808078964991916,-0.1632975363912743,-0.24805517688995882,-0.3328965793954506,-0.42331511472628236,-0.5252857470014718,-0.6403233436901692,-0.7622366170746451,-0.8770752062094875,-0.9664846104216398,-1.0133004238736323,-1.0072823070514696,-0.9487834731322657,-0.8489196568913508,-0.7261384525681422,-0.6004211494830276,-0.4872407323936232,-0.3935617897742303,-0.3172895284712236,-0.2501873411590101,-0.1829301126695979,-0.11015043670429914,-0.033385198407931416,0.03928339381198587,0.09673196381140858,0.12998631417688578,0.13692803500579664,0.12451004019322398,0.1074475688081431,0.1037505700324659,0.12873219092921273,0.1897608900997021,0.2837666685318827,0.3984532556992977,0.5166918083289334,0.6223927621900645,0.7056360370499712,0.7651187108343049,0.8070627714612204,0.8411453423120752,0.8751966462285306,0.9108873691567685,0.9422090733466706,0.9574070439370428,0.9436116276109345,0.8922987502668778,0.8034056572582529,0.6865036880763089],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=4","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[5.879828741772096,5.723684944424338,5.564919034717484,5.405287615415519,5.246875209974377,5.092092146564724,4.943655173439945,4.804546034740408,4.677943045572257,4.567120898175266,4.4753146866562545,4.405545664614189,4.360408768005911,4.341825638785639,4.350771871227595,4.386993354512391,4.448748389221656,4.532810844813912,4.634893013277516,4.750143492373074,4.873588620047045,5.000504620600418,5.12671443494951,5.248806696645397,5.364276715061822,5.471590800773641,5.570176158374724,5.660339316717575,5.74311715203231,5.820066490320642,5.893001544577461,5.96369348171465,6.03355350613943,6.103329968324751,6.172860705100469,6.24095696127736,6.305593589211606,6.364345953453986,6.4148589511706895,6.45527159344706,6.484555617589533,6.502739129116825,6.51099724395559,6.511601248774515,6.50772643883592,6.503127171113509,6.501696264117567,6.50693847950454,6.521501446900843,6.547022552377477,6.101743942952618,6.170066285289676,6.219591383202151,6.250977680328067,6.2659653602492105,6.267250979972175,6.257994311081833,6.241256977277889,6.219539143177324,6.194444308974291,6.166489252021625,6.135068025432309,6.098571020386865,6.054651956833938,6.000626656609064,5.933977068904017,5.852922089199586,5.75696588950724,5.647101205867781,5.525598774378168,5.395669412032708,5.2610911299200485,5.125838350762745,4.993740002771914,4.868184535225848,4.751883097110591,4.646697269002982,4.553534562066633,4.472312966795951,4.401994655091324,4.340688005214141,4.285815939106026,4.234346690290113,4.183080205450835,4.128979247612083,4.069527932593617,4.003040362354105,3.928733988138434,3.8466290758021366,3.757397508226621,3.662195051125944,3.5624967627493516,3.4599483111916736,3.356240325414143,3.2530086498943227,3.1517603858862326,3.053823678413531,2.960318116876881,2.872142141022751,2.789973795802151],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=4","opacity":1.0,"showlegend":true,"visible":false,"x":[3.5404561478325185],"y":[4.20264814790707],"type":"scatter"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=5","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.8058939849264664,-0.7960315845297341,-0.7959096937375497,-0.8117139867550043,-0.8466854864932157,-0.9007480575613653,-0.9706102891924125,-1.0503208653451255,-1.132189934762805,-1.2079359773164562,-1.2698861296461592,-1.3120525160699712,-1.3309284870305458,-1.3258933909762431,-1.2991756597874171,-1.255392174732945,-1.2007456881822178,-1.1420003263035543,-1.0853873526043294,-1.0356291193876705,-0.9952352796130896,-0.9641745049280097,-0.9399654383705565,-0.9181648667282823,-0.8931692728164325,-0.8591976965021454,-0.8112967579606015,-0.7462070659023943,-0.6629544029663659,-0.56307541940423,-0.45044716008801333,-0.3307230743174048,-0.2104314258142841,-0.09593391948829777,0.007560062924240496,0.09677519512086596,0.17092963068137557,0.23197216022392175,0.2843544440119118,0.33436702315818195,0.3891483267033497,0.4555239385656681,0.5388591872106723,0.6421076217002947,0.7652110551914755,0.9049575519544744,1.055339421320078,1.2083805010048922,1.3552529439119245,1.487385541735744],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=5","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.9529757210514018,-0.896257476825588,-0.855768123088547,-0.8356249564817634,-0.8368005525325716,-0.8569536290343533,-0.8907802808869084,-0.9308299618753549,-0.9686551892424534,-0.996109996119628,-1.006588523280688,-0.9960057518099592,-0.9633655751283536,-0.9108302224045339,-0.8432883314849808,-0.7675032303562999,-0.6909901786090098,-0.6207597567973024,-0.5620870191113019,-0.5175827821888237,-0.4867366654299452,-0.46599689501663666,-0.4493674350169403,-0.42942214396400713,-0.39857101311936804,-0.350375779233596,-0.2807075814668658,-0.18856869778065377,-0.07645905197614433,0.049753345235272084,0.1814214926181581,0.3082025197943128,0.41965122536169486,0.5068960767829336,0.5641018956526314,0.5895120041763982,0.5856448873501616,0.5586578521393033,0.517264716639869,0.4713841794538216,0.43069847374539183,0.40332245501515507,0.3947694153472554,0.40735385402395163,0.4401007291180705,0.48914690737834166,0.5485372518395266,0.6112525883019084,0.6703699209055509,0.7203307392755409],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=5","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.6456240110092503,0.5108912875898357,0.3845572412004181,0.271027754398546,0.1735693164124814,0.09403007839608013,0.03270022906352188,-0.011672515544019824,-0.04171193565869635,-0.06110239679691554,-0.07416844214850538,-0.08538770897697101,-0.09888863107758505,-0.11798840776642217,-0.1448256862580416,-0.1801363946423803,-0.22320460106366802,-0.2719239932892146,-0.3228995440851658,-0.371692640465553,-0.413218377737605,-0.44224693910886304,-0.4539517161798866,-0.44444350293248747,-0.4112322454713989,-0.3535653774638555,-0.2726040936169649,-0.1714148935337818,-0.054771859775615495,0.0712163337324132,0.199623737665241,0.3233267561361677,0.43567549913066905,0.5311544993279258,0.6059751659229955,0.6585331818771776,0.6895862363551377,0.702138766650793,0.7011329691775519,0.6929749911476519,0.6849289050126337,0.6844271183865585,0.6983572099327533,0.7323907028037981,0.7904184918888819,0.8741506378773636,0.9829257427760545,1.1137567031285986,1.2615759664267243,1.4195873223142734],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=5","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-1.1646356046215842,-1.1597771613323007,-1.170422385605647,-1.1940786446739453,-1.2232841944338169,-1.247667680343938,-1.2567727693144957,-1.242945660334523,-1.2035649445893044,-1.1420494541621142,-1.0673735052643742,-0.9921805377775756,-0.9299295291892902,-0.8917519267474492,-0.8837821919001536,-0.9056320255622938,-0.950414290949172,-1.0061781180811338,-1.0582796688115386,-1.0923808718004568,-1.0974282584526585,-1.0678837207841494,-1.0046722918181938,-0.914629883564498,-0.8085981727086676,-0.6986376098192701,-0.5950356754559302,-0.5038269908008145,-0.4254055243997159,-0.35452974820189076,-0.28167725311747227,-0.19556096527889677,-0.08642041504299214,0.0509578108089237,0.2152868119159359,0.39833017702982687,0.5861812199563201,0.7619680095948096,0.9092492123344407,1.0153343124066767,1.073795674912101,1.0856233230428076,1.0587853143072226,1.0063232601241432,0.9434468504711548,0.8843140044735702,0.8392418939613369,0.8129765750461382,0.8044189171299718,0.80788312991755],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=5","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-1.5636980004973322,-1.504667381918487,-1.435994078818407,-1.354237493496632,-1.2566079753348032,-1.1415602805647391,-1.0092582758496103,-0.8618406398733762,-0.7034410395609191,-0.5399467950899202,-0.37851357928918167,-0.22688590987511437,-0.09259983438997269,0.01783835913529147,0.09969787909784084,0.1506012024114507,0.17085925927275702,0.16349788438091362,0.13394779375672422,0.08945650924605564,0.038295609558678334,-0.01114689268852087,-0.05128298639867307,-0.07614092844812398,-0.08198371550566913,-0.06765663894183688,-0.034625608582290024,0.013291181598453994,0.07045379398343837,0.13011127887019336,0.18518867310674803,0.2291492408450041,0.25696306388097523,0.26590075412837244,0.2560010842885354,0.23016373492233105,0.19374710194359168,0.15374247135006208,0.11775366081303057,0.09292001010078998,0.08491215757964982,0.09712501804968793,0.13017098612769196,0.18174108827848018,0.24685696935610912,0.3184879172189534,0.3884608970417431,0.44855310834322853,0.491612123944029,0.5125250669955103],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=5","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[6.597104567533039,6.458592465956468,6.314222885524656,6.165126356924852,6.012738132613691,5.85880863205245,5.7053991524775025,5.554857924983656,5.409771302781305,5.272885010344755,5.146991190907552,5.03477874387941,4.938647447305872,4.8604908938183895,4.80145949103243,4.761722553109143,4.740270250607933,4.734968918623298,4.742996987325901,4.761336419677615,4.787190981668237,4.818311564431616,4.8532174348142085,4.8913077535153215,4.932862111151966,4.978932643002691,5.031134121986967,5.091342907399503,5.161321137335792,5.242289004631531,5.334484845663015,5.436941568928736,5.547710496748168,5.664184235511376,5.783357920509535,5.902046181553647,6.017092339466086,6.125602178034202,6.225192855596025,6.314219779591802,6.391948738930194,6.458649100755947,6.51559192809538,6.564944229655722,6.609557575696781,6.652656577317007,6.697440691517194,6.746625156194639,6.802056093465325,6.8646360036415635,5.586672956572552,5.657310494191146,5.707753639101652,5.73772563819518,5.748109921169657,5.740936182589992,5.7189562716027895,5.685125488077387,5.642168205091851,5.592253653132436,5.53679456688849,5.476374306827757,5.410801679073093,5.339286552034765,5.2607229586927495,5.1740593423491115,5.078728064108786,4.975057598462273,4.864355508232654,4.748660985266467,4.630499818444913,4.512694983620957,4.398208024265235,4.2899772061290244,4.190714891741552,4.102680166644134,4.027462685448508,3.9658069729584624,3.917498757162885,3.8813283424691396,3.8551406152478638,3.8359765903585465,3.8203068224095875,3.804351867927563,3.78447882317689,3.7576540694137837,3.7218441655461882,3.676097986253575,3.62040339461513,3.555492633634322,3.4826370629107295,3.4034526025616127,3.319729058157094,3.233289932421146,3.1458845075681987,3.05911073812557,2.9743655400441247,2.892818087369027,2.8154014487914845,2.7428180763093124],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=5","opacity":1.0,"showlegend":true,"visible":false,"x":[5.915544456967698],"y":[3.7145500599253864],"type":"scatter"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=6","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[1.5014101392697508,1.4654597249308314,1.414922520315048,1.350414764264698,1.2729031790099365,1.1837024783372745,1.0844576922891236,0.9771104925302421,0.8638497700285465,0.7470478465171874,0.6291848076144604,0.5127644422867521,0.4002260806568009,0.2938571727486571,0.1957116954785546,0.1075393870804427,0.030730174172264868,-0.0337254024121576,-0.08525963622635552,-0.12372957777963733,-0.14939608859966436,-0.16288157332560949,-0.16510927887594218,-0.15722820898654155,-0.14052862985608794,-0.1163537745093629,-0.08601364809534473,-0.0507067773828242,-0.011455345852286913,0.03094155178724184,0.0759322738061689,0.12320272187790648,0.17261900960830412,0.22413479504578981,0.27766888128279354,0.3329689023331315,0.38955192753680734,0.44672021650133475,0.5035746706519728,0.5590223300847644,0.6117860827275515,0.6604236180878069,0.7033613596290431,0.7389477661451582,0.7655290944965785,0.781549562667958,0.7856769429965873,0.7769515884070917,0.754891815097694,0.7194359975015305],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=6","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.030714054309109326,-0.0017967724754751196,-0.02529864792489983,-0.03460908041071385,-0.025359391828354075,0.0053862016468640694,0.05866324372748383,0.1333527667585444,0.22617539530433406,0.3319384771730551,0.4440095482039507,0.5549613948511546,0.6573128174473768,0.7442776059979088,0.8104336733772302,0.8522347809060297,0.8683072055548463,0.8594976251211333,0.8286695948870314,0.780283789535683,0.7198199986606445,0.6531154739176204,0.5857026789948766,0.5222271238076339,0.46601317361982403,0.41882430353043015,0.3808371184924815,0.3508191983180807,0.3264733142530885,0.3048883849553863,0.28302508370125,0.2581881039618579,0.22845112193456787,0.19293825567722833,0.1519126775624558,0.10666890022079348,0.05924386469917621,0.011996645321116703,-0.03286749413028702,-0.07375409843483688,-0.11004681500622268,-0.14232638217446303,-0.17240310040408088,-0.20315045655663183,-0.23815543005159753,-0.28122703484157796,-0.335825242709277,-0.40448522011651245,-0.48832803010317505,-0.5867519702294088],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=6","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-1.0959070364559353,-1.1837718059396898,-1.2855167586397631,-1.3913685245495808,-1.490028710474792,-1.5700021103492208,-1.6209467211845145,-1.6348771607398873,-1.6070738815451007,-1.536590262666234,-1.4263028057304523,-1.282509088258708,-1.1141358866606703,-0.9316683283106932,-0.7459437543974401,-0.5669670353759634,-0.40289635743336655,-0.259325999356275,-0.13894859000551602,-0.04161429917028825,0.03524517350445078,0.09590617153963898,0.14547125400395267,0.18895046025051387,0.23043987000329086,0.27251195009802043,0.31589609322376533,0.3594806229865838,0.40061621585361207,0.435652579592538,0.460606703697071,0.4719198908706791,0.46727977845415647,0.4462751634008849,0.4107542179506408,0.36483104859404736,0.3143885499474821,0.26616265045925613,0.22668659898242693,0.20125062527181914,0.19301421415059417,0.20239524009742138,0.22682814534694495,0.26093631494703295,0.29710814533267005,0.32640965153483603,0.33971669299742957,0.3289133440492704,0.2879673988082081,0.21368434736028297],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=6","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.6859686957062052,-0.6530923114512411,-0.6143966301584531,-0.5725777613219561,-0.5303434257220501,-0.4900687878514023,-0.4535082373367616,-0.4215931554593284,-0.3943352875036483,-0.3708431750999338,-0.3494466194492777,-0.32791279600171774,-0.3037287278390748,-0.2744193644471059,-0.2378691233512601,-0.19261759206486118,-0.13810184889657118,-0.074760856320225,-0.003937030149247067,0.07232364558781323,0.151524372521602,0.23100094950337768,0.3082079455588248,0.38097715453505554,0.44771936901362164,0.5075459002942929,0.5602948679464431,0.6064580609436461,0.6470158619084074,0.683198954616243,0.7162059042475378,0.7469290000590021,0.7757483082499091,0.8024066455172927,0.8259875092030979,0.8449988654029696,0.8574462816010229,0.8609023764348251,0.8526780642318768,0.8300824919755488,0.7907328152089932,0.7328714767678066,0.6556493965529551,0.5593384585881662,0.4454454751623377,0.31671155723702715,0.1769943178820863,0.03104358204043378,-0.11582130038154415,-0.2581266935287898],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=6","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.0990945446160012,-0.05478041733104744,-0.17837544561213542,-0.2680604145890515,-0.32269778218321266,-0.3436010171628239,-0.33427536167822514,-0.2999696532956695,-0.24708646441343785,-0.18251158370845155,-0.1129314478547746,-0.04420775486008699,0.019127899422965444,0.07420924036892862,0.1199679694558865,0.15705224019555597,0.18754297599675074,0.21452629760623665,0.2415940539343312,0.2722962076091363,0.3095987192126344,0.355412328371267,0.4102488563695561,0.4730466650853711,0.5411875555633846,0.6107056977606338,0.6766674213412815,0.7336811440292568,0.7764814127256885,0.800521575635249,0.8025077788873998,0.7808262792533884,0.7358311929423036,0.6699351671098223,0.5874782970713304,0.494388292062978,0.3976890644585163,0.30490442306985577,0.22339352672924173,0.15968449960409004,0.11887652658569692,0.10417388104194414,0.11660233439200074,0.15494065512378252,0.2158793057717736,0.29439716907992874,0.3843274269486463,0.4790653685343297,0.5722995950499848,0.6585943399265572],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=6","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[6.184732534053777,6.117070841836798,6.04598470131922,5.971973254041631,5.89569963889174,5.8180019783243395,5.73989749480339,5.662576916791322,5.587385995409042,5.515790797748399,5.449323595595962,5.389506785482738,5.337753537345662,5.295245954500293,5.262794566957911,5.240686959570309,5.228546049905443,5.22532684668071,5.22953887639039,5.239506384475378,5.253591944426224,5.270373894937296,5.288772555356667,5.308122702465235,5.328191630401677,5.349143518786639,5.371452171604988,5.395765850605045,5.422730237636328,5.452778673795082,5.485907555350123,5.521547202830074,5.558646060860566,5.595811775753826,5.631436870420612,5.663818731055677,5.69129490067763,5.712395933871579,5.7259963715021405,5.731446006406218,5.728668225872712,5.718216153194623,5.701280596317893,5.679646576027022,5.655597794550709,5.631771222920401,5.610967356157333,5.595925247404899,5.589064079650803,5.592183698993074,4.401907018593774,4.46900985813848,4.525545676274649,4.5712330251915905,4.6064334583519315,4.632169690884214,4.649882304487544,4.661123097416409,4.667301522927197,4.669495565400596,4.668331316373074,4.663932869319203,4.655942051257701,4.643605647664299,4.625925770965301,4.601866548757276,4.570607181544452,4.531803684211383,4.485680808743269,4.432939905823349,4.3746621405438955,4.312236560183756,4.247285265115821,4.18153625992962,4.1166668756180504,4.054153019551975,3.995139789588581,3.940343895183274,3.889994869990743,3.843819424365655,3.8010713100353826,3.7606074183278797,3.721009109271561,3.680745592522708,3.6383732841210725,3.592760513698559,3.5432796732594922,3.4898270605644846,3.4327286749532986,3.3726275439534503,3.310372755559327,3.2469197764559126,3.183247346530214,3.120292940692842,3.058906486456977,2.9998205833024354,2.943634702063706,2.890810564753464,2.841675956812484,2.7964344764374323],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=6","opacity":1.0,"showlegend":true,"visible":false,"x":[2.745669727375028],"y":[2.923531982028244],"type":"scatter"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=7","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.19299024106148532,-0.10004670314413477,-0.010090168769787855,0.0729011924474694,0.14491529978047457,0.20217480572263602,0.24141537146329517,0.26015270081383557,0.25691711455730815,0.23143567888862426,0.1847445925910498,0.11921843321276748,0.038507588837662254,-0.05261970666776561,-0.14852938347630573,-0.2430620030824011,-0.3299470683914958,-0.4031946175988841,-0.4573763254803267,-0.4878939748617337,-0.49125941298189657,-0.4653729696404538,-0.4097941056124219,-0.32600646832475766,-0.21761173578378257,-0.09007730417031978,0.049899229133844925,0.19506186836039707,0.33826729036397396,0.4731630222905595,0.5948673547487441,0.7004079205838797,0.7886116116405611,0.8598030154511563,0.9154685138719199,0.9578939312584965,0.9898916586664928,1.0146104643630285,1.0353214881284623,1.055183080011121,1.0770072249436553,1.103050664430911,1.1348525050888645,1.17313732622546,1.217798872826268,1.2679747612760721,1.322217722144687,1.3787593611792217,1.435728357311292,1.4910749767536915],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=7","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.6135977652980659,-0.7229431650109704,-0.8206769474835738,-0.8974143740072544,-0.9450877347697032,-0.9578833310685202,-0.9329249002686053,-0.8706134487562247,-0.7745798319284316,-0.6512583063958441,-0.5091393836141354,-0.35780168646966537,-0.2068495195606621,-0.06489196973535849,0.06131042787094265,0.16743242180834983,0.25184300772245916,0.3154920854926495,0.36143158119901275,0.3940900807753711,0.4184202164600821,0.43903583237058585,0.45945261258694226,0.4815264403627446,0.5051638866353607,0.5283914307228561,0.5477552546675843,0.5589383302643771,0.5575049592956858,0.5396755943220897,0.5030331785584115,0.447037503575594,0.3732419012958599,0.28525783963152884,0.18851953878718009,0.08986616753590226,-0.00321411211744671,-0.08356330063260309,-0.14523135254610242,-0.18413946697884942,-0.19847091459295463,-0.18876094450136893,-0.15769103810577167,-0.10962548821600837,-0.04995493456770905,0.015671965781320907,0.08214361687021388,0.14562676110298334,0.20406880222476964,0.2572020145505287],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=7","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-1.1068881924280811,-1.0294576133923168,-0.9558241239463355,-0.8892274047440895,-0.8304345714832159,-0.7773443653534486,-0.7255108229022722,-0.669506198292554,-0.6047724199992752,-0.5294312626396528,-0.44549353567442096,-0.35904269022131474,-0.2792361442459036,-0.21629610079849937,-0.17895806382125512,-0.1720226506621545,-0.194666222037152,-0.24008912466565513,-0.29674736583166683,-0.35079659931962537,-0.3891476996258083,-0.4023985085822679,-0.38691423851521356,-0.3455379754356418,-0.2867262862308513,-0.22212835357319083,-0.1632560560946077,-0.11827410750700373,-0.089743360228558,-0.07390020083470672,-0.06167005344438303,-0.04116397512495151,-0.001010721228341005,0.06636414137811952,0.16241556301104332,0.2817388753244767,0.41285113491837055,0.540339829510263,0.6481094518911772,0.7228985828893255,0.7571515240710318,0.7505208726511596,0.709648124707138,0.6463204596314203,0.5745156398380797,0.5071173363052397,0.4531435446323506,0.41616945849755105,0.3942531357394332,0.3812269651380453],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=7","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-1.1237115805553017,-1.1272811037441646,-1.097628777978179,-1.0459713487192666,-0.986191331039648,-0.9326538076628269,-0.8978579090693494,-0.8903167651043405,-0.9130368579563718,-0.9628779098377543,-1.0309314663100544,-1.1038840389733484,-1.16615889683149,-1.202489898837756,-1.2004968693682894,-1.1528210720214136,-1.0584472320313076,-0.9230032298863782,-0.758001191346944,-0.5790988509746289,-0.4036630782704189,-0.2480571461793828,-0.12512493836203264,-0.04231629163188433,-0.0007647070236770359,0.004651575779974992,-0.01573552288568303,-0.048330978464038,-0.07877729965065505,-0.0945569736050833,-0.08723610070406274,-0.05393885180590985,0.002226973364439555,0.07283864174002375,0.1457984795638072,0.2076366589552241,0.24587564201306256,0.2510447851689168,0.2181589714980987,0.1474033345568313,0.0438958592821046,-0.08341959104858532,-0.22352944471166092,-0.3654105879981091,-0.4999894074068303,-0.6216094627111755,-0.7287033831028027,-0.8235123354106264,-0.9110688253538883,-0.9979913607514022],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=7","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.6814081489441037,-0.7163400642331983,-0.739213822743615,-0.7476618257205211,-0.7395518209438223,-0.7134499877224351,-0.6691413365208263,-0.6080794912954206,-0.5336388504159628,-0.4510710017443021,-0.36711922988808554,-0.28931034387785254,-0.22500925670643157,-0.1803756147294106,-0.15939218024159318,-0.1631347164188589,-0.18942228439946962,-0.23293821289051553,-0.28583563448769933,-0.3387403161529394,-0.3820049026433786,-0.4070292598738352,-0.4074489697011452,-0.38001596494139067,-0.32503437463262014,-0.24623138096446906,-0.15010639949698273,-0.0449314964854175,0.06042296833793892,0.1576426643353715,0.23991741503712438,0.3026085593082501,0.34364482001303553,0.3635280684845466,0.3649696676772655,0.3522673086314986,0.3304425665891649,0.3043197150412022,0.27782690190363657,0.2536241677461571,0.23307687200522323,0.21652756774268195,0.20376562927369007,0.19456232833802922,0.1891354251899295,0.18843190572159518,0.19416485212333562,0.20859878885096422,0.23408864754753544,0.27238514999011315],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=7","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[6.508958126564162,6.408558844651116,6.299639203643293,6.182480511441747,6.05764607068696,5.926023274839881,5.788857500205727,5.647771826138925,5.504765524169902,5.362183581723069,5.222649664169403,5.088956401571277,4.96391036213817,4.850135229507676,4.74984606287787,4.664620048804745,4.595215467522117,4.54164539103693,4.503585668592251,4.4807564290363775,4.473128218036828,4.480927698455155,4.504446189252032,4.543680281036149,4.597937178996509,4.665863172313989,4.7458072002202805,4.836083676461141,4.935051565208114,5.041007339536925,5.151929189928936,5.265287745728499,5.378161278290685,5.4874084954815014,5.589779646680886,5.682002784024148,5.760923644972414,5.823739557521482,5.868283727901077,5.893301359150439,5.898673371788739,5.885557348672539,5.856426106125573,5.814992474234103,5.76601583996399,5.714993421202607,5.667748482576115,5.6299386026950815,5.606501391924936,5.601030190599446,4.284351235369802,4.386019278007182,4.468420844199696,4.531031467470775,4.574718745974307,4.601785680792973,4.615418117154045,4.618989241145032,4.615492928394624,4.607132459148087,4.595073155288467,4.579360668994705,4.559001633080164,4.532198872634271,4.4967278127686825,4.45043280430625,4.391811262020639,4.3205818893229075,4.237796624525191,4.145497098546789,4.0463930759081865,3.9436458660212845,3.840666601096081,3.7407788927879295,3.646868437851495,3.5611406094296543,3.4850045896021604,3.4190645799250117,3.363165863031277,3.316423654322972,3.2772116753915057,3.2431722072817477,3.211320383587341,3.1782914831477043,3.1407519903042207,3.0959642212677023,3.042334071598776,2.9794953397843256,2.9080729023778185,2.829400641500897,2.7452498357473916,2.6575926144014472,2.5684126235585367,2.4795657647388394,2.3926877801191893,2.3091420461160923,2.229999512393312,2.156042638090863,2.0877859000075074,2.025506582168317],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=7","opacity":1.0,"showlegend":true,"visible":false,"x":[2.4355048520970453],"y":[3.043692509144023],"type":"scatter"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=8","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[1.2688532417839444,1.0571548438408085,0.8466272025631479,0.6543039406079176,0.49239266828485484,0.36709411521968804,0.2784449646702035,0.22111971799261043,0.18597139521808048,0.1619878190110613,0.13830388698437257,0.10594052835842904,0.059024860630008336,-0.00463876404484842,-0.0836563650429476,-0.17369746403632635,-0.26854437168165146,-0.3612260918095548,-0.44495047196408843,-0.5138574583785769,-0.5635668045559382,-0.5914934022703832,-0.5968490643086176,-0.580269803403037,-0.5433203761113321,-0.48800750545001226,-0.41638051191857994,-0.33030134127519695,-0.23142231504256303,-0.12138448049024628,-0.0022162231212927985,0.12331381206469451,0.25171910347061155,0.3789903005555321,0.5009492714230958,0.6137670462540568,0.7140134854591809,0.7983283401969352,0.863375483804321,0.9060858001017111,0.9240646151422323,0.9160306205442978,0.8821645564098748,0.8242784013713598,0.745765042104878,0.6513448057759057,0.5466761099925657,0.4379196142635131,0.33107503204946265,0.23065048888382567],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=8","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.38698645084973204,0.3128702769844444,0.27661223195581147,0.2927419415521467,0.3481247821224386,0.40353890930810554,0.40760697798174206,0.31779880101905683,0.11976326785357938,-0.16344459640398168,-0.47664320693345197,-0.7506616271929034,-0.926241706748459,-0.9741552603198302,-0.9035888794235035,-0.7558004843103588,-0.5861872862444735,-0.44266611119916816,-0.34943113714948976,-0.3021739187573795,-0.27570485590090177,-0.2395469775419769,-0.17378787833779008,-0.07785991168894213,0.031146917402957497,0.12906720898412388,0.19839704012483095,0.23810443886871002,0.26460610753921454,0.3034665142857126,0.37600565624557236,0.487494705578039,0.6228890893409105,0.7526419128823756,0.8461456164977305,0.8864749535517953,0.879265623236156,0.8511092658693806,0.837687943054762,0.8668048472912177,0.9441235697752032,1.0485082795724292,1.1396866829377177,1.175373682314529,1.130530853090406,1.0101764260098607,0.8497699477088335,0.7025769130318594,0.6186308522533793,0.623060170129987],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=8","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.8229734693411436,0.7678406204943252,0.6553639148554169,0.48947023270668866,0.28282196634685447,0.054891273619730174,-0.1712520273801922,-0.37287703859859667,-0.5315462286812652,-0.6363662536014542,-0.6859321721494229,-0.6885914385171947,-0.6609499783899107,-0.6248479001476354,-0.6032881377420299,-0.6159587880700051,-0.6750638851575111,-0.7826688411743734,-0.9305134071342716,-1.101654261450303,-1.2735969074705205,-1.4225939288605023,-1.52760766871761,-1.572174135612366,-1.545291033488645,-1.4423303741425386,-1.2656328046816148,-1.024112883834503,-0.7320580984339133,-0.4075437589217189,-0.07090853139507175,0.25697542196378265,0.5572129688168651,0.8150465522453249,1.0212911088402186,1.1730829192061063,1.2730070833416518,1.3269878302991378,1.3423516112819123,1.3263528882914837,1.2852048899692905,1.223590681423235,1.1445778828457684,1.049832535798548,0.9400256536239935,0.8153445308651516,0.6760502375147294,0.5230447635251199,0.3582304452992752,0.1842820783896051],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=8","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.4676211907989179,0.40246999733421224,0.3096844716531038,0.19849268136514095,0.08174109890677214,-0.02646042654605202,-0.11350209175923759,-0.17089336608125197,-0.19618636090355063,-0.193769283100687,-0.1743093120481059,-0.15289175070323346,-0.14617000965778928,-0.16905404795782292,-0.23157915827857473,-0.3365883865701088,-0.478715595433384,-0.6447144840416306,-0.8149188655324228,-0.9658282133038562,-1.0733886938272854,-1.1163346609344955,-1.0793336997816925,-0.9558847866133218,-0.7500003709812664,-0.4755311957013355,-0.15350775957851703,0.19128442008146163,0.533943208417154,0.8528787315496946,1.1326876650690707,1.3655455086532784,1.5501749334358808,1.6897555973106924,1.7896126558286458,1.8550526393636813,1.889858671772691,1.8956514255699703,1.8720038090050393,1.8172081925206187,1.7294834784361959,1.6083222215639577,1.4556618214677417,1.2766187462260747,1.0796353595746297,0.8760285435434091,0.6790666722717709,0.5027976442334353,0.3606318429332811,0.2634473970211688],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=8","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.05346090084318772,0.14038885681421043,0.22858905939707552,0.3162111306029475,0.40069847233012695,0.4788517129000962,0.5470138764575949,0.601356335016344,0.6382292676346943,0.6545309930817668,0.6480487399364956,0.6177296119590762,0.5638539281387812,0.48810189861971187,0.3935260504689988,0.2844628319906157,0.16641994591044962,0.04579353007267839,-0.07071373871164477,-0.1766796303000968,-0.26646750027069,-0.33568195801099043,-0.38147553592406647,-0.40260400955061326,-0.3994509774723848,-0.37356524589700346,-0.32688001140449824,-0.26124894895599926,-0.17838871715727553,-0.08022706954088157,0.030386684868617286,0.1491935260378644,0.27102597601272704,0.3906752993619542,0.5039759376909474,0.6090315467736742,0.7059808985196306,0.7955199828909204,0.8778622889851717,0.9522805556867906,1.0171051697131852,1.0700471552310198,1.1087111010486739,1.1311672359232796,1.1364633143862832,1.1249755350126842,1.0985214375042092,1.0601841401796679,1.0138376852262434,0.963397986365123],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=8","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[7.25505299557851,7.137551682383661,7.003065586816941,6.850757197833216,6.680245524148064,6.491760340924872,6.286298647605154,6.065765746217712,5.83307632485728,5.592184327451336,5.348006307706342,5.1062047928424725,4.872810809967363,4.653694310285095,4.453943872902459,4.277295204125445,4.1258701171820285,4.000820440853111,3.9037247422528303,3.8373529148411953,3.8052959931501005,3.810574933351678,3.8541959386697613,3.934633645627583,4.047576706081331,4.186818119196312,4.346050724332167,4.52015823126421,4.705617420523785,4.899987273532085,5.100712445487534,5.304208480937758,5.506177597643976,5.702026516161326,5.886748949195261,6.054451127081881,6.198242314874243,6.310870077358628,6.385734591063956,6.417950774314065,6.405252403102528,6.348620080091091,6.252572137625074,6.125090798253921,5.977178017209505,5.822060393541326,5.67410182130605,5.547534687975744,5.455024839002489,5.405759381958511,4.277924512377107,4.46449311228622,4.616210139485795,4.730391078807945,4.808057387340481,4.854646701482398,4.878434025762911,4.888301415636657,4.89192192709032,4.894461110972527,4.897822756403338,4.900440855165586,4.89760854833719,4.882326422378506,4.846633699544046,4.783344583071062,4.688041952330253,4.560869038892449,4.406431335216315,4.232053896327058,4.0464433215186,3.8590580262815575,3.679628066453743,3.517018185795305,3.3779759398107783,3.266404455070053,3.1833198578428874,3.1274012229332975,3.095792161838991,3.0846330951460037,3.08922608254278,3.1039919010735906,3.1220928447985687,3.1352892952286235,3.1346636420994924,3.1124180221880318,3.0640731210223864,2.988994020737389,2.8895771002806843,2.7702234564161756,2.6363705655647864,2.4936984627503653,2.3475533670792377,2.202582875946002,2.0625503393526308,1.9302858513170351,1.8077314225398453,1.6960435364851105,1.5957241282641816,1.5067590267691822],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=8","opacity":1.0,"showlegend":true,"visible":false,"x":[4.5153938687938275],"y":[7.49092917848877],"type":"scatter"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=9","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-2.0366306407999164,-1.9591818022327914,-1.8046937050027605,-1.587710989592634,-1.3402087237989075,-1.102084959459448,-0.9081219238221232,-0.7764751130382934,-0.7032686841683486,-0.66554105464534,-0.6315146645529675,-0.574255959378505,-0.4833996482030627,-0.37027982394670644,-0.2642553390494049,-0.2012396321660681,-0.20831078350326715,-0.2916988114807433,-0.43434921932474224,-0.6015162246129424,-0.7519680460358236,-0.8511360154997065,-0.8814190586448376,-0.8460128382436312,-0.7656684414783728,-0.6677524845330289,-0.5724726281732195,-0.4837619978066243,-0.3879751769184838,-0.2602158889815729,-0.0751375124154996,0.18138999880915918,0.5028577134384768,0.8600203433234586,1.2067026893648287,1.4906542974446708,1.6684992798223472,1.7197198075180564,1.653075609721376,1.50223855134265,1.3104837945514527,1.1148532601973251,0.9364832153182361,0.7792736986192264,0.6359680883792569,0.4980365068146808,0.3645712554170819,0.246195036188241,0.1622397354635794,0.13238718501427904],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=9","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[1.5389082846616484,1.458308557000201,1.3294722108228738,1.1586061507241163,0.9562231139438465,0.7358048372173946,0.5118790195596491,0.2978828925623487,0.10423641291183738,-0.06299666916105412,-0.20260837830383122,-0.3178309096158699,-0.41511001774452017,-0.5023111223501396,-0.5866673629599103,-0.6727558353111418,-0.7607524181460883,-0.8459773615864499,-0.9205300779830558,-0.9756778430567629,-1.004509176096717,-1.0047578644591042,-0.979847146807015,-0.9358769992844661,-0.8777523309275325,-0.8075928439448803,-0.7251439985357244,-0.6285034269121527,-0.5150235685758497,-0.3823813772937994,-0.22970046758224494,-0.058491433875310195,0.12683570004660494,0.3188892791836164,0.5075779020954683,0.6807765778627526,0.8261391706174228,0.9337779419920409,0.998700928978089,1.0217982088589372,1.0082977588629338,0.9654272674699942,0.9001898696007631,0.817574133650024,0.7195214775955714,0.6049024979830939,0.4706120535155165,0.3136968012839718,0.13358568211358834,-0.06719862794029163],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=9","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.18423776970785766,-0.23021550265748225,-0.2722528677398952,-0.3018040773011772,-0.3107710182941261,-0.2945139594786045,-0.25383881891796545,-0.19528906675607582,-0.12964218523327542,-0.0691101692947853,-0.02417107116958417,-0.001069295182782426,-0.0007732455259789051,-0.01964301067948948,-0.05140395152507504,-0.08945013050851347,-0.12830653846156587,-0.16465216008382305,-0.19862938421595044,-0.2334794823632245,-0.2737021624876965,-0.32312008595406283,-0.38262425006718637,-0.44672251700630117,-0.5021032533345652,-0.5298673051671026,-0.5102720010482336,-0.4278295048004098,-0.2753887733656304,-0.05634822329914557,0.21524008447605125,0.5170695396816201,0.8236059650917933,1.111314101912958,1.3625751296287685,1.5676811459903637,1.7239106979357026,1.832456317597628,1.8952831065645572,1.912895974825348,1.8835082151124318,1.8038893305935486,1.6715217916235776,1.4872484016223022,1.25752890841032,0.9957154673791528,0.7223286105223823,0.4648796966164239,0.2550270764038829,0.11824759450215461],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=9","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.3499304407586731,-0.5287212617724562,-0.6556448505179491,-0.7360070806117645,-0.7751097386094343,-0.7762896663730676,-0.7407674188728053,-0.6691616954383766,-0.5639200974470846,-0.43160283472362737,-0.28402574952396553,-0.13767875080881797,-0.011424202049814314,0.07697434785575219,0.11464383911874287,0.09692972830634972,0.029736099976651276,-0.07115960605288024,-0.18511087831124867,-0.2921288250290628,-0.37723938336442275,-0.4334033586676307,-0.4616743082183328,-0.4675906421139012,-0.4573434302719702,-0.4340593669625441,-0.3953019671750999,-0.3336285412489083,-0.23947899807974415,-0.10467786024242787,0.07542521933832524,0.30047829759827294,0.5621691663652387,0.8435350617004114,1.1210048323196005,1.367707871578441,1.5597158864442258,1.6832062860437524,1.7380334512367182,1.7362573967553887,1.695515695531007,1.6312844019730326,1.550898018197435,1.4508794722010068,1.3183055026185693,1.135980111129029,0.8903865527967765,0.5808366212290914,0.22440196884081587,-0.1516545670303433],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=9","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[0.4558976356439053,0.21147991557031628,0.021789663195677045,-0.09973582148649884,-0.14809089514848095,-0.1274948720374105,-0.050971303383477884,0.06124612209665736,0.18427312343478264,0.29175601804218954,0.3592479341633168,0.3673376059516662,0.30414371067464285,0.16690818247798553,-0.03740797026483142,-0.29242540509903237,-0.573339037389764,-0.8495100952854553,-1.0893772409292573,-1.2655532355226426,-1.3592797641332333,-1.3640932349328572,-1.2867422976697884,-1.1431302267237926,-0.9526732080898761,-0.734368410521431,-0.5045980232994122,-0.2754366352859534,-0.05377319326444241,0.1582795742226596,0.3614052364264073,0.556892048849494,0.7462134819193299,0.9304455287234753,1.108996900740977,1.2783109590869228,1.4314236481370157,1.5588967713836808,1.6511965922864504,1.700771618318056,1.701686898733215,1.6494093131755987,1.54149428729,1.3786947442744353,1.16608340625996,0.9139269581678695,0.6382276683572372,0.3609692719421417,0.1085061723127792,-0.0948728617911761],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=9","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[11.883401498927746,11.573254841945296,11.20851176446407,10.786082907901966,10.304972518114692,9.767093835999152,9.178096534615705,8.54807856255988,7.891992991676303,7.229498674349257,6.583962127135022,5.980333264421032,5.441745503372584,4.985006319874859,4.61572525905208,4.324701015302489,4.0884432370181,3.879122547206477,3.680547872167468,3.49606637484856,3.3446804911744037,3.2489617573019305,3.2243070789518797,3.275593479788058,3.3948632582116396,3.5652703276372018,3.7718672056901674,4.009624090005277,4.283846949960568,4.602682166530621,4.965807435360566,5.3597719379391675,5.7663124255336555,6.1708233373105426,6.56318676148459,6.9333898929280195,7.271310212612353,7.568840826375143,7.815442774946349,7.9913773028052795,8.069261563787231,8.02238630996145,7.834103965504324,7.504568878390485,7.0530015235923145,6.515458291968082,5.939797516475663,5.38101865278652,4.898686620375203,4.549773016916674,3.768871669994112,4.394021480645078,4.954817275497169,5.439007237292357,5.838324794308706,6.159411659898872,6.42029596458346,6.639371407537654,6.825820541689008,6.974552452658624,7.067103955370733,7.078376513709,6.987396559801369,6.788468859066758,6.49519806109064,6.131165547477493,5.7210286055265716,5.289115433043287,4.857291799771986,4.439977187823161,4.044368927451473,3.6779138832482126,3.355840906463056,3.097496230288278,2.916404428502661,2.8134285552582767,2.7770841475352155,2.790642683167867,2.841283824678819,2.9231413925707246,3.035049989153327,3.1774241653316277,3.3437057301449995,3.5112149916757973,3.6399984447713774,3.683567199458939,3.6071713286401597,3.3969468560224847,3.0582657523272827,2.610462240490886,2.0807885771788714,1.4990946189779573,0.8938816623496026,0.28982384317906007,-0.2934469708099652,-0.841610836022979,-1.345306580370126,-1.7994290549558434,-2.202282143263047,-2.5547265688445977],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=9","opacity":1.0,"showlegend":true,"visible":false,"x":[5.035550221532578],"y":[8.35378853998293],"type":"scatter"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=10","showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.7741987493301814,-1.0149662580283245,-1.189513011566567,-1.2433761628129198,-1.171080383554016,-1.0173317203868895,-0.8572553745320042,-0.764093094273869,-0.777978349705199,-0.888939345715631,-1.0413346154160275,-1.1579635098786096,-1.1738249351060106,-1.06535030464959,-0.8626395149177528,-0.6390947707821829,-0.4821191269418378,-0.45717497157195275,-0.5805298479107234,-0.811226983679202,-1.0660488943399615,-1.252311160259405,-1.3041684089772239,-1.2056441451853726,-0.9931809447634009,-0.7387083834534424,-0.5195184320978594,-0.3859684532188432,-0.34079531140342856,-0.33925200819727935,-0.31059214398014023,-0.19104560587157637,0.04741001848075199,0.38358081624686147,0.7555459754356666,1.0886791921169063,1.3262605815869986,1.4486887840972162,1.4751315068791575,1.449317221537242,1.4204126703616886,1.4194836846011603,1.442026457000777,1.4461689491694476,1.364513946079997,1.1301561498549058,0.7095940861043704,0.12837832334861554,-0.5251615002131103,-1.128022286950988],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=10","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[1.2637352457109285,1.1649456010474362,1.0205161693602123,0.8499900911779438,0.673787685864222,0.5098808335735503,0.37105423242013447,0.26324527758351635,0.18523692261839053,0.12970730374863204,0.08537060906105909,0.0397300330570991,-0.018151010664668732,-0.09544545929957593,-0.19438392274769933,-0.3123330584861823,-0.4430652928492007,-0.5785760874681878,-0.7106166902462401,-0.8316838783789597,-0.9349172289674681,-1.0124903290584926,-1.0552106587923942,-1.056938933443408,-1.019206508523439,-0.9499359583660141,-0.8580101799447992,-0.749149246046271,-0.6241507951242808,-0.47970643526354095,-0.3116623240180645,-0.11858518255142458,0.09724712752017384,0.3296795203331453,0.5691139234372827,0.8040591885468793,1.0220685467450965,1.210500503309565,1.3591210080126466,1.4622235243591915,1.5171749630629363,1.521586639294779,1.469554132981,1.3489011341874586,1.1453378469588569,0.8496087734822273,0.46456590747063764,0.012995306818029073,-0.4603836447099081,-0.9059141302511069],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=10","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[1.1711302009208773,1.0320753377875675,0.8961188036074693,0.7684916303595013,0.6490874465393821,0.5338137129662138,0.4167149367862548,0.29230936731045254,0.15757605762189175,0.013149130421384436,-0.13651597026136086,-0.2839981825891478,-0.42056663581458786,-0.5382733565610167,-0.632081077559739,-0.7016912573363154,-0.7528016786810929,-0.7965512985750616,-0.846191357425476,-0.912764635121291,-1.0004985709519143,-1.1021979429483106,-1.1986104251602177,-1.2664092139531526,-1.288256943252317,-1.2563482244085225,-1.1704283129549455,-1.0358333688726038,-0.8617574854094969,-0.6591676667688641,-0.437929895036564,-0.20488244108114728,0.03470753725023906,0.2755960742836172,0.512267739888249,0.7394387356092418,0.9521841649558528,1.1451273213050075,1.310769163724827,1.4387311085181567,1.5179854757379372,1.5385079989225017,1.4910995316145312,1.3665314445135517,1.1563842838690561,0.8553410022675826,0.46489562882194146,-0.0007719182079142239,-0.5121815079727566,-1.0360050662752736],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=10","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[-0.26740810308365237,-0.6886598380781104,-1.0244708899889718,-1.232788497450318,-1.2995195992246429,-1.2394260550828826,-1.0898763845038881,-0.8995416355944443,-0.7154225813220796,-0.5718880035118556,-0.4846231251101263,-0.4507813760822814,-0.4546873472656525,-0.47673066354246885,-0.5021148686178565,-0.5261499579686313,-0.5539310536289266,-0.5961015841767954,-0.6639955808309432,-0.763867939337755,-0.8926716478699561,-1.0384019429450548,-1.1826808407112375,-1.3007257005215798,-1.3636589348422339,-1.3461170883999207,-1.2353180117735443,-1.035958547093907,-0.769439293149349,-0.46787218748360404,-0.16467924900606912,0.114483698826231,0.35651035132353615,0.5616961557395168,0.7411971055436815,0.9117542219996109,1.0881929248460995,1.27547932903208,1.462666384837413,1.6227858879613546,1.7219203652256763,1.7302249755047088,1.6308795259267765,1.4247801001604476,1.1283485780531148,0.7676317871120846,0.3728552150387556,-0.023701609698114967,-0.3904824210797182,-0.7106114373670613],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"hoverinfo":"skip","marker":{"color":"red"},"mode":"lines","name":"a=10","showlegend":false,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0],"y":[1.6458764096322844,1.5087993695306001,1.322833584663352,1.0854518767850947,0.804994824391552,0.49926500922209205,0.19235901190765337,-0.08972345573859608,-0.3239304198177153,-0.4946056145914285,-0.5967097351981696,-0.6371611298929837,-0.6339120983898048,-0.6126986199045787,-0.6017168032413908,-0.6247310341535128,-0.6934884256111107,-0.803402819869028,-0.9361034567520683,-1.0653363017968114,-1.1654344527726597,-1.2224533118715106,-1.2397679693929988,-1.2280530027590042,-1.1922891333491137,-1.129452859328163,-1.0342775480565631,-0.9036413162848644,-0.7386619290219127,-0.5451243962081951,-0.33304939520391796,-0.11488751510343498,0.09858911793475822,0.30167967077866353,0.4949228973995574,0.6839328283050365,0.8761927571270189,1.0762791363068307,1.28024009644168,1.4722358773675028,1.626848005761878,1.7146663112312397,1.7105078895908181,1.6014845275959364,1.3872180825809808,1.07696607556655,0.6875408425003418,0.2409665481718153,-0.2376260307483422,-0.7196524074395967],"type":"scatter","xaxis":"x2","yaxis":"y2"},{"fill":"toself","hoverinfo":"skip","name":"p=10","opacity":0.6,"showlegend":true,"visible":false,"x":[0.0,0.12244897959183673,0.24489795918367346,0.36734693877551017,0.4897959183673469,0.6122448979591837,0.7346938775510203,0.8571428571428571,0.9795918367346939,1.1020408163265305,1.2244897959183674,1.346938775510204,1.4693877551020407,1.5918367346938775,1.7142857142857142,1.836734693877551,1.9591836734693877,2.0816326530612246,2.204081632653061,2.326530612244898,2.4489795918367347,2.571428571428571,2.693877551020408,2.816326530612245,2.9387755102040813,3.061224489795918,3.183673469387755,3.306122448979592,3.4285714285714284,3.5510204081632653,3.673469387755102,3.7959183673469385,3.9183673469387754,4.040816326530612,4.163265306122449,4.285714285714286,4.408163265306122,4.530612244897959,4.653061224489796,4.775510204081632,4.8979591836734695,5.020408163265306,5.142857142857142,5.26530612244898,5.387755102040816,5.5102040816326525,5.63265306122449,5.755102040816326,5.877551020408163,6.0,6.0,5.877551020408163,5.755102040816326,5.63265306122449,5.5102040816326525,5.387755102040816,5.26530612244898,5.142857142857142,5.020408163265306,4.8979591836734695,4.775510204081632,4.653061224489796,4.530612244897959,4.408163265306122,4.285714285714286,4.163265306122449,4.040816326530612,3.9183673469387754,3.7959183673469385,3.673469387755102,3.5510204081632653,3.4285714285714284,3.306122448979592,3.183673469387755,3.061224489795918,2.9387755102040813,2.816326530612245,2.693877551020408,2.571428571428571,2.4489795918367347,2.326530612244898,2.204081632653061,2.0816326530612246,1.9591836734693877,1.836734693877551,1.7142857142857142,1.5918367346938775,1.4693877551020407,1.346938775510204,1.2244897959183674,1.1020408163265305,0.9795918367346939,0.8571428571428571,0.7346938775510203,0.6122448979591837,0.4897959183673469,0.36734693877551017,0.24489795918367346,0.12244897959183673,0.0],"y":[18.338065481744763,17.427615671766084,16.417416088487727,15.314346266669592,14.131239295945079,12.887686261920866,11.610414190349033,10.332968023486782,9.094391849782058,7.936615492508028,6.900349241934507,6.019524555368391,5.314751421396943,4.786940336256132,4.413144357826833,4.147638597404472,3.9320282966156146,3.718448064089602,3.4929510013171514,3.2760539397777237,3.101946373960347,2.9938601180304407,2.9593488796892826,3.001831963511977,3.11606858889696,3.282756326781617,3.4815572418422023,3.7070569264459867,3.9716959056203227,4.291780635037977,4.666937150514814,5.0761441392356526,5.498228455654141,5.926336384449383,6.360555550074437,6.792171443088367,7.2056939457578295,7.5890697725443514,7.927475476871721,8.195182254357563,8.366620651717986,8.425634938448406,8.355672721872622,8.125918341804226,7.70253432035509,7.07178966067408,6.25142602356157,5.291000342665118,4.274385793055321,3.3151812996124463,3.107659452193013,4.186558028721026,5.219185639111165,6.158336462449998,6.946806324758837,7.556395365172216,7.985256017671233,8.238498113646834,8.323438115594135,8.25969738170461,8.081521621768013,7.820586574725808,7.49481230500878,7.116557895132225,6.7031398412094,6.269521045280971,5.823543608736872,5.377473859490353,4.950743444044229,4.554252455990262,4.182838611307936,3.829427337239616,3.505278927036325,3.236444129571852,3.0437673064873065,2.9291425153662978,2.8783524198667463,2.87656332286926,2.920377208414964,3.0102576431327632,3.1423985267282357,3.317600976107925,3.5392277793343196,3.7935055210751942,4.03341221902894,4.183934530527716,4.169249629416374,3.935290302321866,3.4571568515507236,2.73804520897638,1.8035075280583799,0.6939290342417923,-0.5428279656997868,-1.8575464893554532,-3.2041362822354102,-4.542485271369539,-5.839915824302907,-7.071568354377181,-8.220038746668326,-9.274555360610885],"type":"scatter"},{"marker":{"size":10},"mode":"markers","name":"i=10","opacity":1.0,"showlegend":true,"visible":false,"x":[5.143971561084619],"y":[8.298211828582026],"type":"scatter"}],                        {"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}},"xaxis":{"anchor":"y","domain":[0.0,0.98],"matches":"x2","showticklabels":false,"range":[-1,7],"title":{"text":"X"}},"yaxis":{"anchor":"x","domain":[0.575,1.0]},"xaxis2":{"anchor":"y2","domain":[0.0,0.98],"range":[-1,7]},"yaxis2":{"anchor":"x2","domain":[0.0,0.425]},"annotations":[{"font":{"size":16},"showarrow":false,"text":"Surrogate","textangle":90,"x":0.98,"xanchor":"left","xref":"paper","y":0.7875,"yanchor":"middle","yref":"paper"},{"font":{"size":16},"showarrow":false,"text":"Acquisition","textangle":90,"x":0.98,"xanchor":"left","xref":"paper","y":0.2125,"yanchor":"middle","yref":"paper"}],"title":{"text":"Gold Search"},"sliders":[{"active":0,"steps":[{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"0"}],"label":"i = 0","method":"update"},{"args":[{"visible":[true,true,true,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"4"}],"label":"i = 0","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"11"}],"label":"i = 1","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"18"}],"label":"i = 2","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"25"}],"label":"i = 3","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false,false,false,false,false,false,false,false],"title":"32"}],"label":"i = 4","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,true,true,true,true,true,true,true,false,false,false,false,false,false,false],"title":"39"}],"label":"i = 5","method":"update"},{"args":[{"visible":[true,true,true,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,false,false,false,false,false,false,true,true,true,true,true,true,true,true],"title":"46"}],"label":"i = 6","method":"update"}]}]},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>

### Random
Choose the next point by uniformly sampling a point from the domain.

In [51]:
generation_strategy = create_generation_strategy(
    botorch_acqf_class=None,
    random_class=Models.UNIFORM,
    random_trials=10,
)
ax_client = create_client(generation_strategy=generation_strategy)
predictions, acquisitions = run_ax(n=10, ax_client=ax_client, acqf_n=0)
results["Random"] = ax_client.get_trials_data_frame()

[WARNING 08-11 10:42:46] ax.service.ax_client: Random seed set to 1. Note that this setting only affects the Sobol quasi-random generator and BoTorch-powered Bayesian optimization models. For the latter models, setting random seed to the same number for two optimizations will make the generated trials similar, but not exactly the same, and over time the trials will diverge more.
[INFO 08-11 10:42:46] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[RangeParameter(name='x', parameter_type=FLOAT, range=[0.0, 6.0])], parameter_constraints=[]).
[WARNING 08-11 10:42:46] ax.service.utils.report_utils: Column reason missing for all trials. Not appending column.


### Comparison
Compare the acquisition methods from above by showing the max gold achieved against how many trials in the experiment.

In [52]:
max_gold = {"Method": [], "Trial": [], "Max Gold": []}
for k, v in results.items():
    max_gold["Method"].extend([k] * (len(v) + 1))
    max_gold["Trial"].extend([0] + (v.trial_index + 1).to_list())
    max_gold["Max Gold"].extend([0] + v["gold"].cummax().tolist())
render_plotly_html(px.line(max_gold, x="Trial", y="Max Gold", color="Method"))

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="0955c146-f7a8-4173-9fbb-eddb3db851fd" class="plotly-graph-div" style="height:100%; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("0955c146-f7a8-4173-9fbb-eddb3db851fd")) {                    Plotly.newPlot(                        "0955c146-f7a8-4173-9fbb-eddb3db851fd",                        [{"hovertemplate":"Method=PI\u003cbr\u003eTrial=%{x}\u003cbr\u003eMax Gold=%{y}\u003cextra\u003e\u003c\u002fextra\u003e","legendgroup":"PI","line":{"color":"#636efa","dash":"solid"},"marker":{"symbol":"circle"},"mode":"lines","name":"PI","orientation":"v","showlegend":true,"x":[0,1,2,3,4,5,6,7,8,9,10],"xaxis":"x","y":[0.0,4.153277647970732,6.4030358079544385,6.4030358079544385,7.78026814236398,7.78026814236398,7.78026814236398,7.97083381305886,8.353438586358578,8.353817966113354,8.353817966113354],"yaxis":"y","type":"scatter"},{"hovertemplate":"Method=EI\u003cbr\u003eTrial=%{x}\u003cbr\u003eMax Gold=%{y}\u003cextra\u003e\u003c\u002fextra\u003e","legendgroup":"EI","line":{"color":"#EF553B","dash":"solid"},"marker":{"symbol":"circle"},"mode":"lines","name":"EI","orientation":"v","showlegend":true,"x":[0,1,2,3,4,5,6,7,8,9,10],"xaxis":"x","y":[0.0,4.153277647970732,6.4030358079544385,6.4030358079544385,6.4030358079544385,6.4030358079544385,6.4030358079544385,6.909021517750929,7.691138525684522,8.331261799710944,8.348254087751911],"yaxis":"y","type":"scatter"},{"hovertemplate":"Method=UCB\u003cbr\u003eTrial=%{x}\u003cbr\u003eMax Gold=%{y}\u003cextra\u003e\u003c\u002fextra\u003e","legendgroup":"UCB","line":{"color":"#00cc96","dash":"solid"},"marker":{"symbol":"circle"},"mode":"lines","name":"UCB","orientation":"v","showlegend":true,"x":[0,1,2,3,4,5,6,7,8,9,10],"xaxis":"x","y":[0.0,4.153277647970732,6.4030358079544385,6.4030358079544385,8.062511138469858,8.062511138469858,8.353042361423036,8.353042361423036,8.353042361423036,8.353604872575431,8.353772660864934],"yaxis":"y","type":"scatter"},{"hovertemplate":"Method=Thompson\u003cbr\u003eTrial=%{x}\u003cbr\u003eMax Gold=%{y}\u003cextra\u003e\u003c\u002fextra\u003e","legendgroup":"Thompson","line":{"color":"#ab63fa","dash":"solid"},"marker":{"symbol":"circle"},"mode":"lines","name":"Thompson","orientation":"v","showlegend":true,"x":[0,1,2,3,4,5,6,7,8,9,10],"xaxis":"x","y":[0.0,4.153277647970732,6.4030358079544385,6.4030358079544385,6.4030358079544385,6.4030358079544385,6.4030358079544385,6.4030358079544385,7.49092917848877,8.35378853998293,8.35378853998293],"yaxis":"y","type":"scatter"},{"hovertemplate":"Method=Random\u003cbr\u003eTrial=%{x}\u003cbr\u003eMax Gold=%{y}\u003cextra\u003e\u003c\u002fextra\u003e","legendgroup":"Random","line":{"color":"#FFA15A","dash":"solid"},"marker":{"symbol":"circle"},"mode":"lines","name":"Random","orientation":"v","showlegend":true,"x":[0,1,2,3,4,5,6,7,8,9,10],"xaxis":"x","y":[0.0,5.057664805217066,5.091532753266253,5.703244208949001,5.776814007863983,5.776814007863983,5.776814007863983,5.776814007863983,5.776814007863983,6.01297425838335,6.01297425838335],"yaxis":"y","type":"scatter"}],                        {"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}},"xaxis":{"anchor":"y","domain":[0.0,1.0],"title":{"text":"Trial"}},"yaxis":{"anchor":"x","domain":[0.0,1.0],"title":{"text":"Max Gold"}},"legend":{"title":{"text":"Method"},"tracegroupgap":0},"margin":{"t":60}},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>

## Hyperparameter Tuning

In [53]:
# Import moons and SVC from sklearn
from sklearn.datasets import make_moons
from sklearn.svm import SVC
from sklearn.metrics import accuracy_score
from sklearn.model_selection import train_test_split

In [54]:
def create_svc_data() -> Tuple[np.ndarray, np.ndarray]:
    return make_moons(n_samples=1000, noise=0.5)

In [55]:
X_train, _, y_train, _ = train_test_split(*create_svc_data())
render_plotly_html(px.scatter(x=X_train[:, 0], y=X_train[:, 1], color=y_train))

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="a802eb49-8864-4f3e-96bf-11774b3b4529" class="plotly-graph-div" style="height:100%; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("a802eb49-8864-4f3e-96bf-11774b3b4529")) {                    Plotly.newPlot(                        "a802eb49-8864-4f3e-96bf-11774b3b4529",                        [{"hovertemplate":"x=%{x}\u003cbr\u003ey=%{y}\u003cbr\u003ecolor=%{marker.color}\u003cextra\u003e\u003c\u002fextra\u003e","legendgroup":"","marker":{"color":[1,0,1,1,1,1,0,1,1,1,1,1,0,1,0,0,0,0,1,1,0,0,0,1,0,1,1,0,1,0,1,0,0,0,0,0,0,1,1,1,0,1,0,1,0,1,1,0,0,1,1,0,1,1,0,0,0,1,1,1,0,0,0,0,1,0,0,0,1,1,1,1,0,0,0,1,0,1,1,1,0,1,1,1,1,1,0,0,0,1,0,1,0,1,0,0,0,0,0,1,1,1,1,1,0,1,0,1,0,1,1,1,0,1,0,0,0,0,0,1,0,0,0,0,0,0,1,0,0,0,0,1,0,1,1,0,0,1,0,0,0,1,0,0,0,1,0,1,0,0,1,0,0,1,1,1,0,0,1,1,1,0,1,1,1,0,1,0,0,1,0,1,1,1,1,0,1,1,0,1,1,1,0,1,1,0,1,1,1,0,0,1,0,0,0,1,1,1,0,0,0,0,1,0,1,0,1,1,0,1,0,0,0,1,0,0,0,1,0,1,0,0,1,1,0,1,1,1,0,0,0,0,1,1,1,1,0,0,0,1,0,1,0,1,0,1,0,0,0,1,0,1,1,1,0,1,0,1,0,0,0,0,1,0,1,1,0,0,0,0,1,0,1,1,0,1,1,0,0,0,0,0,0,1,0,1,1,0,0,0,1,0,0,1,1,0,0,1,1,0,1,1,0,0,1,1,1,0,0,0,0,0,0,0,1,0,0,0,1,1,1,1,1,0,1,1,0,1,1,1,0,0,0,0,1,0,0,1,1,0,0,1,0,1,1,1,1,0,0,0,0,1,0,1,0,0,0,0,0,1,1,0,1,1,0,0,1,0,0,1,1,0,1,0,1,0,1,0,0,0,1,0,1,0,0,1,1,0,1,1,0,0,1,1,1,1,0,1,0,0,0,0,1,0,0,1,0,0,1,0,0,0,0,1,0,0,1,0,1,1,1,0,0,1,1,1,0,1,1,0,0,1,1,1,1,1,0,1,0,1,0,1,0,0,1,0,0,0,0,1,0,0,1,0,0,1,1,0,0,1,1,1,0,0,1,1,1,1,1,0,1,1,1,1,1,0,1,1,1,1,0,0,1,1,0,0,1,1,1,1,0,1,1,0,0,1,0,0,1,0,0,1,1,0,1,0,0,1,1,0,0,1,0,1,1,0,1,0,1,0,1,0,0,0,0,0,1,1,1,1,0,0,0,1,0,0,0,1,0,1,0,1,0,1,0,0,0,1,1,1,0,0,0,1,1,1,1,1,0,1,0,1,0,1,0,0,1,1,1,1,0,0,0,1,0,0,1,0,1,0,1,1,1,0,1,1,1,1,1,1,0,0,0,1,0,1,0,1,1,1,1,1,1,1,0,1,0,1,1,0,1,0,0,1,1,0,1,1,0,1,1,1,0,0,0,0,0,1,0,1,0,0,0,1,1,0,0,0,1,0,1,1,1,1,0,0,1,1,1,1,1,0,1,0,0,1,0,1,0,0,0,1,1,0,0,0,0,1,1,1,0,1,0,1,1,1,0,0,1,1,0,0,1,0,1,0,1,1,1,1,0,1,1,1,1,0,0,1,0,1,0,1,1,0,1,1,0,1,1,1,1,0,1,1,1,0,1,0,1,0,1,0,1,1,1,1,0,0,1,1,0,1,0,0,0,1,1,1,1,1,1,0,0,0,0,1,0,1,0,1],"coloraxis":"coloraxis","symbol":"circle"},"mode":"markers","name":"","orientation":"v","showlegend":false,"x":[0.1784252967699646,1.4286119269724442,2.272797379055794,1.2518417987497337,2.9950282580630763,0.5959022393785125,0.34472140705604665,2.5176215315221455,1.0175936183997576,-0.037376529976069994,0.14646563737341411,0.5240627819962048,0.9418869051194192,1.2208337000331664,-0.7540839732440623,0.6648277031989744,0.3761084026450429,-0.7342223776885495,1.3151959000217979,0.3498272130764298,-0.5095995807360327,0.3573772852959673,1.3503843683517225,0.8167595626993702,0.21249126969343285,2.3326238817557248,0.91052461278338,-0.06323947880081049,1.8405961727522615,0.020501665409823344,1.7757180076550618,-1.7337102821060846,0.16789810592780852,0.425785973342957,-0.5144430252284176,1.5831649332749032,0.32966407480510806,0.47876715541361786,0.629556497374133,1.769008552772915,1.3274009457603286,0.498877716065605,-1.4061098962556307,1.4653154304753844,1.2436672364386752,1.4070430967650251,1.6170450078968435,1.1902627024297812,-0.24061633786724174,0.9493749028508733,0.289272288776024,-0.43910062851206755,0.5299594415869379,-0.4159320151201382,0.18811473046533086,0.550339200699864,0.5457608391276484,0.11905747632437086,1.8954657861234376,0.12622130163077228,-1.3637694232906021,0.9811470140150162,-1.5618995546457997,-0.4279828089155254,1.432797831729397,0.8910099764816902,-0.508649383779781,-0.6448291837211443,1.978213496995665,0.5034299590561413,2.6760746181337423,1.4629946806549912,0.192783717054532,0.033612615095160114,-1.2535973926325634,1.8777206709985328,-0.8377382089767201,1.0324539879310788,0.8647950244620456,1.655020558017669,0.7735041054951913,1.766448834343354,1.0499932258928308,0.12066613702557588,-0.4695336627124851,0.8007240315370276,0.03731057676605086,-0.4746972118707299,-0.706388902595205,0.3491380430047732,0.4048581247429939,1.8981690815265049,-0.299156757932755,1.5128614111348002,-0.3674540194404442,1.704753228268529,0.9964614814502909,-0.19494660938990893,0.6357804031543878,1.6994392919585375,0.9592155348591709,1.9289115239116985,0.8564063157080255,1.8612470660654439,0.8865230249525458,1.620423670600098,0.3267063123626074,1.2840470417667948,0.5695925845708338,1.909465297015911,1.6970287120871919,-0.9227423639490503,-1.0362167771753836,1.36937387424135,-0.05437057106530596,-0.10117387048487803,0.9395169936700273,-0.09694377196650916,-0.8023697078606342,1.2571887654754175,-0.5782401350391213,0.07844852953503156,1.357329508308736,-0.8981737354182395,0.9423315585034355,0.3079698656233477,0.2187273448478208,0.08713712177820965,1.602348894656803,-1.5265056231115444,-1.2066988776974314,1.2529846268423603,0.248166869013834,1.2848155551389475,1.3506263867340158,-0.12654239779638451,1.0552506152646572,1.5057705234778893,0.12859246603914198,-0.650472640158025,-0.6300814635774195,1.3282136280441819,0.8932202589906153,-0.47540723928532747,-1.6035239325914965,-0.32327288114007746,0.18405430101873113,2.1066662303410064,-0.440621642017961,0.6107355343131785,0.7332948177364663,-0.03469766448442346,0.19465743084165138,1.042969402032473,0.42860561921810925,0.8821837622453318,0.7554908316319016,-0.9624969869390035,1.9610484660787955,0.03340178969348301,0.733650930667076,-0.259268967582647,1.8236099105316728,0.5310363801031972,0.4814788545328308,0.42112913992948264,1.7567661831924481,-1.6527490592505252,-1.3319999881344713,1.559899706362306,-0.9133505486750297,0.3900704550162747,1.563302707372233,-0.12533818884958053,1.0352464045243148,0.31869749844421136,1.8028390010311173,0.5537275506102856,-0.01995016688621727,2.2365737657163907,1.4129889351365317,0.6886257192399934,-1.5206529921327059,1.1377331889436015,1.4492230757842504,-0.02761110410327311,0.2234080732202849,1.12196293177628,2.1703117410733004,1.2932812518003427,0.44639539007196893,-0.6869878366042014,0.8174822459248783,1.6455004134366975,1.349074994558658,2.136962065409501,0.3857138089979638,0.09847309556032532,-1.2011479220787962,0.7274131350443536,0.7185587138623428,-1.5100977259929915,1.8127258739240626,0.5082125037162295,1.7992443025678213,0.7206042510802743,1.3094568561098263,-0.8959646608940459,0.7956438938360093,0.6429208237211206,-0.16957771639127378,1.8003890418907043,-0.4881897061365839,1.1863379220344956,0.35259055495981195,0.6280991082394609,-0.820238527734801,-0.6919507146282262,-0.7835434848613829,1.1762780227710663,1.3024269920359224,1.488609602505877,-0.5254833440139615,1.9579824395665166,0.5119777888497801,0.061352908655554095,-0.5367679711878026,0.9019660805726263,1.200907152124809,0.7528330720255313,0.3036297511368232,0.025029043262870254,0.8301957044126054,1.7581617797220068,1.053320151127455,1.8668676505540023,1.205080852652924,-0.8193760420459231,0.5185631499171769,0.24239439362882112,-1.1444385059549973,-0.23187745277294747,0.8193051341731955,2.222734828345303,1.2891129374189383,0.07687836820815888,0.1231690299284934,0.4710192177709553,0.8725834468814015,1.0241794800160486,-0.24887036865847958,0.7194804847442989,1.4143499296206001,1.567179276104226,1.7757381299407022,2.099241493312478,0.04324663127741332,0.8397958261528772,0.5347271586541991,-0.04493860630191471,0.30443501858408306,-1.2150128163508631,0.6030437232211571,-0.9298205240204636,1.3622021018214228,1.113212502954672,0.6651915061775615,0.1381271932935684,-1.9733017761397678,1.8654327275674745,0.631831219628637,-0.03422800946568122,2.146848578408654,1.5577750900609921,0.5411776264310851,2.098328781681167,0.9428604642328067,-0.09580073478703566,0.6322853526073916,1.0538736331943195,0.8167148234970174,-0.014353846058700381,1.7965668760668254,1.7279105405956392,-1.7749484631168153,0.16789131591986012,0.47879867240577123,-0.23366194774317772,0.4044364517366221,0.08623108966818438,0.6478462053624575,-1.0381048785020488,0.4160469785170649,1.4496221114409105,0.511517845696128,1.4699845351868925,0.5929566762854224,1.7709230167810008,0.24145042301216985,-0.44289969803139473,2.090714818596533,-0.4285340619618898,1.2662869661426592,-0.8496584432008459,1.0248496732081684,2.1225690198840965,0.4703713945423718,-0.5098529654588376,0.5697651371300061,0.043281590723763474,-1.56217116446535,0.08827553767076646,-0.31619112399654326,-0.3053530542528533,2.4540689418517174,-0.6905365082898466,0.7255299798836367,-0.6595079665882317,1.5697163243219234,0.2627304793212536,1.0198751401575117,-0.3489242707143302,1.491471168059417,-0.5436767200530173,0.842285805179604,-0.010195117851771206,0.7005245635762146,1.0263526229092408,-0.3225547029935613,0.9420692552873651,-0.4044869785580138,-0.8783298036266136,-1.8022304035817824,-0.9043298990168479,1.094059011659892,0.4389161945604668,1.7542963518211712,1.6660229140761245,1.2405108241623388,0.381866463751619,0.8155704121653715,-0.9719074952124391,-0.4856647264728138,1.6390693529202935,1.7222628202056989,1.867082927048035,1.256676042861265,1.4816784406666978,0.9549654285365782,-0.3080402052258446,-1.2667922414126602,0.1366928638670633,1.0202424713399176,0.0921540171771636,0.1383635924320048,0.40718048238345117,0.1626860606401096,-1.8788146875129623,0.31160507223629014,2.320266338412174,3.01414724225427,0.2820512706865017,1.7889168189291589,3.1098003287186975,-0.5515696995601922,-0.502103160876597,0.05420394885162124,-1.2593907118977916,-0.6023472223513315,-0.04252380500704159,-0.14945215564733894,-1.2382275926449964,1.865252931093526,0.906144788502455,1.78663713458516,-1.18435854854404,0.8076070220638885,-0.7635946499941433,-0.747680021418456,-0.8116670463794572,-0.7950479821428038,0.5400259006248017,1.9197776933255748,-0.9398176853406183,0.1688950288018859,2.0562718809381813,2.561077281213164,-0.8033307084267778,1.4335155753305715,1.4082705398503237,-0.20142585942605018,-1.4591675085614055,1.445773947445749,1.5802023790161017,2.1790625256306355,2.3718896740657405,-0.9123553658995611,1.545509201441548,0.13810187262149293,-0.13315324348580748,0.9559893098532367,0.8325393310835428,0.6252582575642759,-0.4815538923577928,0.9339129255320215,0.14389752523875782,1.3485938646804227,1.1401279748871103,1.9451097316698491,-0.03150759036593487,-1.0006578934374775,-0.09131931650912169,0.2657151971356959,0.18617378452540312,0.7717575175449726,0.5480640688478938,0.4022496392968289,0.22931136484869358,-0.07817891607713565,-0.6156150344702355,0.18857158613292008,-0.8068019544150516,0.22784405782580341,2.2098403674986136,1.9109589831741376,2.010852660240612,1.267221281553892,0.7479568826717666,1.759551867031004,-0.26459779605034356,0.5426568787885436,1.5049507493454746,1.2958617315672079,0.399142738227502,1.9027083691399829,2.0521217082359877,1.3307416914776158,1.2472835787889687,-0.26070131703811344,1.193348664442389,-0.3666940363151837,0.7732093468161438,-0.6437581711755043,0.43262699004522887,1.234499431875202,-1.2085994896953833,-0.41265401340191527,0.2915363072838303,-0.7050766210091531,-0.19364497340647954,1.0976191327098737,0.27781777569522204,0.8415795152745982,-0.037615327558112366,0.2509484457773131,1.6405948897308154,0.1511693088903432,1.4997974830930874,1.02706773966641,1.0011206585995591,-0.06163013167551373,1.8296179832771449,-0.058303026524943236,-0.1864416262678824,1.5477416190978306,0.5010085027093018,-0.38320695490925905,0.7739067625165542,2.199513074997837,1.3271483578611871,2.9116202160415576,2.3393662786145253,1.8132502549630027,0.30858487154611947,0.6976464797620757,0.1970183709465749,0.6434558488373832,-0.279927496572422,1.1565995306635342,0.5288352561808533,0.5868951457991572,-1.3105257774357824,1.5538530585424435,2.287212607500067,0.2404565004816448,0.7775490706561692,0.9834415402387957,1.0746582788657932,0.4843789697250215,0.20839893340168236,0.32500304294364885,2.35410760345326,2.0013152406708525,-0.9112622716723956,-1.3195486512877361,1.9982382019986544,0.3210824064211992,1.452079135971011,-0.5070982538005983,1.3947398393158301,-1.1562184993395175,1.8500186492187114,0.9294348914568265,0.42009935668792486,0.7132882693575492,-1.1240553093373618,0.9937974894970125,0.14921214290452112,0.9173178166649334,0.32151127346775166,0.9113584259565863,0.5351348300797234,-0.8552600665396765,-0.5226264621438479,-0.2630484961716896,0.22148712026329093,-0.5155735438042727,-1.4461155615911927,1.6648996400368963,0.06490558093086263,0.02408549294668039,-0.1981878700158726,0.21473263891731031,-1.0374991245094116,-0.2640599948422552,-0.8966063381640484,0.5197470290094821,2.263138117920386,0.7600929410344127,-0.06422470616100717,-1.1476646645221746,1.2250752532331481,0.9421135935867703,-0.09874414580347723,0.22636617006667986,0.7516340871600565,-1.1071108782384864,1.3864369987399094,1.042386870689813,1.1291034680969956,0.967461102582145,1.2288685569933302,-1.022458671838164,0.21669275317685632,-0.8189297978976122,-0.6110569927219547,-0.3384407741216129,0.573126313603382,2.109766594917751,0.9092306051389533,-0.3222303345653772,0.31305309676576065,-1.0105580005178902,-0.32456607002762616,0.3792734474923583,2.046397150622276,1.7274396254077544,1.6073977724256672,-1.5301542089714502,-0.40940910563116106,0.13166091094810456,1.3557455320331933,0.07726025447388596,1.3586618978601188,-0.10017710719307261,1.204851477667921,1.252528769057827,2.091622361241292,0.3941029980272321,2.1793906211736243,0.1562778114897085,-0.4828563053670776,0.5404607688916813,1.5616924132070389,0.1712169379016758,0.5505598310743356,0.12443604215321047,-1.2685107297205738,1.4312086096966745,-0.6259949793032858,0.5208451217622725,0.08431573096752443,2.5124667537944,1.031551787657178,1.7818656248209812,1.680104273247413,1.931384660957175,0.8968514755399594,1.8366549881047292,0.5846631760106258,-0.5663533051226564,0.9513887872178202,0.9507915581765408,1.523251868534493,-0.6396793174461721,2.1459866275164203,-0.2251787273488938,-0.13142449708018858,-0.4137447871033227,2.022954182417232,0.721263268728104,1.5643121500743946,-0.05196055936621226,-0.7515609459056638,-0.48190291856655953,-0.2030641701970486,-1.449464716974747,2.0199964798409047,0.20272286438547832,-0.6630464909936858,1.1416589233699743,-0.6714010938644626,0.15311624269744983,2.0205303479362042,1.8470706835971602,0.20281301022317216,0.8284573139737769,0.4142045329443146,0.1313103939052042,1.5777398659300301,1.6952291048650285,1.456315570892568,0.4424283746141188,-1.071121927985048,0.035152296368788055,0.568124105155394,1.0221818747983447,0.4320359177144215,0.7880001427812849,1.6022506278089268,-0.3921934331373592,-1.9045390724127826,-0.8189388239880219,1.6230350343391293,1.809228171562859,1.2380568206312503,1.5871389086816348,-0.012800729021086296,1.4488580199264622,-1.5076543791956407,-0.5403076080081141,0.8893097202925936,2.4113334035257243,1.6920244470933095,-0.1830216939409165,1.0507801724539283,0.9792166665074866,1.287451381994662,1.8497866650447132,1.126836464764229,-0.09240657030205365,0.038102583076273136,0.5420116339879816,-1.0119894866319612,0.11226506351420329,0.7710859139818268,0.5082673124308146,0.36263950254041,-1.6223011838513912,0.5506324744247668,-0.9449260574752925,1.4524722965431733,0.7968673572529895,-1.1098748719241822,-0.8457136478752345,-0.6980026709764964,-0.1559519120901548,0.15914477811635264,0.08488891016874471,0.8633902299386118,0.002016182399453781,0.3245263010363688,-0.4765731049330115,0.6446265770611845,1.023724788860875,1.0032397536495665,0.0011905125890822599,0.6071955721565632,0.13905595314747465,0.4884534758310005,-0.5268801111755024,-1.0800777259478294,1.5061636637867923,1.4656316255775241,0.11334945766116017,-0.7365755266962115,2.429766085848186,1.8403331431843444,1.6579304220014672,-0.3217658754542966,-1.9254486533795767,1.0827279280723179,0.9775436833291474,0.3336853366333379,0.043249147051301326,0.6879879673639687,-0.3629462555159434,-0.5373564272106746,-0.4881936819883598,1.6472354890001555,-1.0136552781159351,2.107556956024386,2.188839598321479,0.014991966041024072,1.6324194763123294,2.290576740989371,0.5337487980193525,1.9284826895913731,2.1459783466496467,-0.4306847830815269,0.285632170605322,-1.7155725753464228,0.3071217025241194,2.4593139291093293,1.5423641215380337,0.13622191964234542,0.2000941555089233,-0.17435741622581236,-0.24054419925531578,1.2507096114219534,0.7682151132867879,-0.9715508854860339,0.1813060835071465,-0.39396874347348254,0.7197640231742183,0.27120549285413564,-0.6871565078053109,0.08233298343111062,0.9648618509816971,0.47299860446756953,0.3119142037467083,-0.2045774235167452,-0.6262338419837172,-1.6598883490539436,-1.3025063368864291,0.9876661682701579,1.5048280694861755,3.0560380046377453,0.7138987188938146,0.45720844278954564,1.0764326024511235,0.8097234816332907,-0.2717547699413052,0.255775167128623,-0.13077099573569073,0.05793008177050285,-0.9795442023040681,0.8377596988338719,1.1482288630802626,1.8856800299238061],"xaxis":"x","y":[0.16346391631565416,0.4243948884205342,0.8510658403289103,-1.2298016858703584,0.733011530583035,-0.19226313658638305,0.8676712772383381,0.3039245228940456,-0.001152565259438687,-0.5248524763526976,-0.2742962183179115,-1.2643754104923963,0.13779015851457332,-0.19504945322956796,1.1367829907827725,-0.26005588645294364,-0.10741120369351381,0.8182667334008262,-0.09095408566568547,-0.2525306695959783,0.5960548836020322,0.4736175611734367,0.6547351225898992,-0.4172022935094322,0.5143488754648434,0.4358130323352998,-0.9651651240600816,0.3283994494263204,0.5571810308450856,0.008604548972020384,-0.07837902352638626,0.26229907422152104,0.7681151872906591,0.9933585597756314,1.1718303835845414,1.0824858265882598,1.0459533694592777,-0.16753450499433356,-0.3311312932468252,-0.3186656599518678,0.8307033977519376,1.011276510552813,0.452500521685385,0.9000693044678847,0.9288295571006417,-0.24672257792660227,0.26794484473499225,1.2972227840974448,0.5559034176847019,-0.9062545017742262,0.29980174822105876,0.9853762178101054,0.5830849708877053,0.8246824882082251,1.2319013930713991,-0.16049529600281842,0.25948030401536504,-0.604729594534683,-0.0587373745473207,-0.033367351867190476,0.19643931961252167,0.9490840461778014,0.16205921334468387,0.7292746209050102,-0.8469158082582758,0.21572704456468716,0.06033978263364825,0.4894685945439192,-0.12677271581111127,-0.3988865596904296,0.4229547315626393,-1.0288926052708256,1.6238237130759612,1.2676511427969526,-0.02051808072696587,-0.7409998211934794,0.7298845575526577,-0.514187220616478,-0.3435616880576672,0.1337384637792648,1.1526116242544715,0.978024535770648,-0.2946879072429217,-0.32554646927074016,0.20968459754201277,-0.7792475002079077,1.516791232476014,1.1212175831708082,0.3261833993560615,0.007479553157847041,0.6900621408396511,0.30247875274007363,1.1649762217166157,-0.024137041542647897,0.8197122903220312,1.3240347666140049,1.0160273375988684,0.8509752556200361,0.4734977831025893,0.28769727354998376,-0.08634305043233648,-0.2749910796101579,-1.1317075648396249,-0.05092125207931053,0.7277249316991058,0.5002296526165448,0.7325080649082478,-1.1615700869659913,-0.06287990410644828,0.9861899230825394,0.15663898039717938,0.44738432901693637,0.571268805171943,-0.0178289896388934,0.30115175683262096,0.06516947781503868,0.830570346353135,1.100175549142636,0.6809584453614297,-0.22993941814831753,0.6096772575769549,0.27475401483648343,0.4320611531167858,0.2813493887460452,1.715269186009965,0.7026484330962144,0.4207208756096457,1.5929131626148358,0.9616469452262623,0.4944492519281397,1.417121252345071,0.08386475939090235,0.21379001554998162,0.6352619327478783,-1.1191155432499962,0.19129387146103904,-0.12363006887290684,0.45379053852122697,0.0615393072919936,-0.22869800063812434,1.057945330071043,-0.3636206306476144,0.4924954691149141,-1.278386273883435,0.7041436230301263,0.12916255002826327,0.9823613557911067,0.40476098093816487,0.7224400050203689,0.9785148527089663,0.06598188477481187,0.9956187148848207,0.0856753008773079,0.24707967923118385,0.790655035821058,-0.44218658857439597,0.15242449136581737,0.3430040655351311,-0.15056923504824124,0.8937543341459612,0.35537052789629486,0.5349848632498934,0.37719766452975867,-0.7631191712475118,0.6158684386477321,0.9372539506112761,0.2639088285793006,0.5724083819809396,1.6270498553800823,-0.04306001724317779,0.6470630181106845,-0.026553634853732133,0.20995202009184466,0.3098247269736051,-0.959412814412144,0.9895058641482529,-0.15564050876825486,-0.49373690822592814,1.4073057328555318,-0.49806019047387595,-0.27428795601212735,0.04505692280108281,0.8816222356068328,-0.15854259234197693,-0.29785973762967904,1.203310165638659,0.17942741004736956,0.23977951871625103,-0.2866190613438339,0.3418451596347178,0.20079208909424534,0.2393630969421457,0.5087763792751967,0.46408521296306304,0.9761357449795282,-0.26899146594571177,-0.9388827866579808,-0.4982887187956965,0.85289062704757,1.2769970520808922,0.6886932798600878,0.46005322499271534,-0.6496526465883896,0.49454584343663144,-0.1656965830027251,0.8323300843841827,0.6506623457404077,0.752169048372686,-0.1537008225365739,-0.7199429168305135,1.5789117873788898,0.08959387207967662,0.7076435728179308,-0.5088377147759491,-0.255093297545904,0.26957059322784427,0.8274296535785253,0.027741791355233275,-0.6300546521693511,-1.2165945227676764,0.05951714021136603,-0.6792029869458134,-0.3557458549297043,-0.8122694871711623,0.9258050986429248,0.39019139252590473,-0.3461944424750959,-0.5857990374625941,-0.2203517760150261,2.060775858608021,0.5747972538655357,0.27852026415977454,-0.47128542468829526,-0.6807504232754924,-1.1528095459201473,0.15389949347964463,0.015156545998472284,0.6750977998693966,0.5176676365175179,-0.11469932860850629,0.34848907879851193,-0.279011101637969,0.5117858878421702,0.4954867227745504,0.33533113881476984,0.2611768389480563,0.6589071335894535,0.8087055260923316,1.3775050203125727,0.32803476881351024,0.7915587525340506,-0.4823812263487288,-0.1196781288809684,0.09341866686851055,-0.1781648526000342,0.2083246936255747,0.8878474826913798,-0.17915739585528495,-0.1170794690084758,1.0233781269117321,1.260435281900734,0.5733304447125518,-1.2354170988332336,0.6868462257345866,-0.6649242063658258,-0.46694481703432594,-1.0814370823008732,0.9624530076234624,-0.27918607113720423,0.4836010077895289,-0.7529943765873478,-0.12306354911197981,0.08683175351650696,-0.5823172452232935,0.2556595279316009,0.580397398920032,-0.7354027426009244,0.04136522931821274,0.899072729192541,0.5739521773260217,1.134212108818202,0.09479984320290752,-0.5353177745661923,-0.1442357851363199,0.09526206590876402,-0.7613451949761468,-1.312481651356582,1.0297644309163978,1.276090384049512,0.489473613678441,0.5311783220052838,-0.6057701238635949,0.6410231574913037,-0.01502791957818822,-0.5560079921408138,0.7984486453796126,0.24091794539526667,-0.7957251639008,0.23941144253182364,1.2921789578580352,-0.5230487026618904,-0.3637506901100468,0.17555858879437258,0.830969780433107,-0.8273252784990407,0.246616886183406,-0.48338186793175897,0.5553165982158295,0.4696570397105567,0.6022673701745267,0.7728064065525476,1.8327729742676935,-0.7987875536017132,-0.28816987621667833,-0.6234303107267947,0.48436021933523077,0.23398509338820017,0.6738561508026439,-0.9896010241659388,0.1127764424513466,-0.12966385335331204,-0.017629205490271187,0.37954637343066333,0.2798788417272863,-0.9352394599984789,-0.2790619242623462,0.724936585253259,-0.0967277418957839,-1.7917927709399262,0.0019720731401320357,0.7466788694993671,0.8597230987668307,0.42085160935750876,1.1077367443192216,0.01225665004358445,0.900119025267178,1.1771751520225926,-0.4822736581697552,-1.4378706907787944,1.8250097966144878,1.2778183824514855,-0.0937049599898907,0.7466496888521313,0.10973283721536942,-0.17571934924681415,1.184018164174264,-1.0032755015793597,0.8472969749290956,-0.007280256498004123,1.987318809874007,0.8313391528471075,-0.824328269063468,0.5221688979082505,-0.2108317559912596,0.2412692499766219,0.4751325567245009,0.8621459473115831,-0.0026700661191616515,1.1529645447388623,-0.2889601790499745,0.9221238326219303,1.282967630724213,1.6912859821229067,0.15965415085485246,0.5324414516848404,1.3053426774321606,0.05293088191440953,0.8065467961905757,0.3948565063889777,-0.7038184524760132,-0.48916822721053393,-0.5446494567147915,-0.9101503156931657,0.3514125165595334,-0.13701732421145327,1.8474542048722795,-0.22548602903490456,0.035941651090025006,1.077456094429065,0.7352802472858118,0.20672958408001305,1.0051173957539559,0.15348113365509714,1.186223489445043,0.16841614139933703,-0.2024149296414463,0.5172363280140148,0.27510791148949143,-0.4683521308639253,0.04704183591730987,0.8959852905576864,0.1440305014378773,-0.12757461106564252,-0.8753609510396522,0.16405294954064042,0.4904529543074732,0.5235700631134593,-0.5145958406523696,0.015860885517657408,0.07711912693963008,0.6104700781297376,0.9384086081105,-0.3989569494782137,-0.22554021324074913,1.605344122690657,-0.007469281054284571,-0.5448802257205174,-0.38063335041511426,-0.9691269360590965,0.4838288841383095,0.6879913842795864,0.9885669993183288,0.8549492512388522,0.2740428969758152,0.21734999491945964,0.47867613561717126,-0.7473850811987905,0.02138584230798568,0.2427072320278877,-1.2701022706805842,-0.7919861644370244,0.6625051952401778,1.1330756123107502,-0.8106637134255039,-0.8049024783789085,0.006955306891988949,0.059252059114260805,-0.213460864989327,-0.37243592752511967,1.4947584195812114,-0.057640475498433985,0.6726945320970039,0.2875780694706081,-0.5553178603250345,0.40829448550136554,-0.027518502828273138,1.2285327722638628,-0.7367792611273201,0.49712249409293824,0.6686296195660808,1.6587694556534291,-0.26306925233809475,0.8734469002989971,1.2501428598207827,0.14904568246052408,0.4888130845618235,0.6206894071796667,1.8129735815481638,-0.30613461965348665,-0.11960725086781909,0.3100106564897395,0.25057113210254855,0.0708140383674494,0.8832859801646624,0.9132329195128248,-1.2274591098874301,-0.6615781877112807,-0.7852311029736159,0.8066205226143321,-0.026358396717725496,0.1972083689142034,-0.17729405050062624,0.3069191419577043,0.7352665127302224,0.2568680712256931,-0.39291439986910476,0.1275329084635164,0.3078458514285908,-0.16327022892320459,0.5943258943325658,0.7868282160795375,1.2399366379528467,-0.06246338594888037,-1.3949985163440277,-0.1395593169416373,0.7737732723888745,0.8139631522362623,0.23561469602333657,0.3738695824079674,-0.22368790017120704,-0.07028699447493372,1.371793257322185,0.030844847946613352,0.3301578369878323,0.5836210256999176,0.7438195426171684,0.8625433569891207,-0.470787742175825,-1.0922332875034968,0.38353278817349357,0.9012124668984948,-0.3098922857523398,-0.13749603405241226,0.02036125594539312,1.2097428804515589,-0.28499472195980907,1.1746285946982027,-0.34345125927307013,-0.44832779064770334,0.7262829997501499,-0.3654315780335754,-0.4035898491020546,0.46721623562847636,0.6816978821352964,0.12650774310331936,0.8289031753950823,0.37527642461772914,-0.9618390210805864,-1.3358960713797905,2.03571391105643,1.1914509038566847,0.18759509901761362,0.7764173944352382,-0.14270032144692207,0.3970770828832967,0.31797408160108276,0.10376680093017643,0.7843443698489466,-0.051582688497236295,1.3160027078903487,0.26114346251718973,1.287615531756188,1.6468434267137104,0.989178240776543,1.6183306725379762,1.4009788517739423,-0.29082172285703933,0.012294223113770208,-0.6047469573461285,-0.015047568729119332,1.4128671433914652,0.2566042040786603,-0.03650093720172881,0.42120507669419177,0.9301805342174727,-0.42843836904130495,0.9855172860045864,-1.5295924686019293,-0.3075153238310857,-0.5822204954779913,1.1079610408417566,-0.3385524332528438,0.7095359182451958,-0.10168918905321199,0.8121166299448929,0.5025549659268582,0.7004893846769122,-0.8934710057318316,0.39202595143545116,-0.11661148658632828,-0.2483313845321431,0.24770378879595722,0.04363130769651313,-1.302373151481079,0.46585009449804393,0.6939463907774007,-1.6228394022822528,-0.1674056992775922,0.6576535922901919,-0.636271245146439,0.1580389777602057,-0.3113701810455904,-0.06677560662796855,-1.5463520538054403,1.1262581166526886,-0.009313023795108788,-0.23933578736001412,-0.3473107529511724,0.7788350688088495,0.24830590238861577,1.4078959419675379,0.008365794741433064,0.26438711479427524,0.31086214900691245,0.5488594313281305,0.9622901572614924,0.1497412950444933,0.2740084313846188,-0.5255572168667254,0.24825423631878685,0.3759017132368854,0.4809901231547154,0.3220038891548755,0.17206754415514866,0.597069821407954,-0.691157190936347,0.15273655505555372,0.43370286479399445,-0.1869445814817156,-0.4159765628479787,2.087681711727333,0.38881913856987826,0.24060227684775876,0.8019245950226703,1.679920540642104,-0.24623085127091893,0.661303536148584,0.2696624337196454,-0.24914715197913018,-0.3680289311887607,0.03241174807698821,0.31926153124874646,0.030220796149751095,0.8661098470321218,0.4166040832087981,-0.8344141209870306,0.2397553740616603,0.21567912927059002,0.2561156871734416,0.43545962143830974,0.16822167011797517,0.16714670305293045,0.19361917088115566,-0.5659272228558678,-0.772371753976286,1.1701220723718946,0.32650237971869805,-0.9058774304884214,0.8427675592826454,-0.06745687533886963,-0.7404928567818564,-0.8763151058470844,1.3427114821328665,0.8102282460139796,1.2594356902000374,-0.14258594745290454,0.1786592855658281,-0.9922556851498754,0.20853978274015822,1.0039217243297618,1.6558239065915856,1.0649577223093316,0.5063366373196168,0.2998215622887568,-0.2815891076409571,0.9634419959115446,1.0417311203458595,1.2933966397132488,-1.0102361522509333,-0.10934167898121083,0.06708030405076618,-0.7822361403669023,0.04546261615861766,-1.2399440290190944,1.058829206621878,-0.40765254367389747,-0.9999836733032422,-0.11090599380126087,-0.6431684862247329,-0.2479166821267321,0.7858949160661006,1.4197503034592627,0.041038048075409644,1.2226601049080916,-0.24339718604555516,-1.2603069944554652,0.4049455923187655,-1.0725788298721215,0.22794497234352862,0.22269918782793602,0.2244190513466926,-0.5281217927737667,-0.43503955946884443,2.044349128077981,1.0983005293635995,1.6343579350500597,0.5800732660798372,0.2416588733090097,-0.44100155382832196,-0.27503541031393186,0.9733730650286166,-0.21360911926024684,1.2787002267350513,-0.11395882055066647,-0.25960072319446303,0.4241423412168794,1.4560676546491744,0.6716199033803575,0.023994991602970084,-0.7606158983351801,1.2520652724882235,0.07807899814737335,0.04443775422645577,1.6287978138033146,0.7152204982823984,1.6147205929218527,-0.30243292595725046,0.4281722113518962,-0.636117073470404,0.0976904584694345,0.0014182488626618417,-0.044487868450446416,-0.25234158981655463,0.4694302576766164,1.005020781707172,1.984716704725845,-0.15742860108922835,0.33587596733118513,0.13124415910904585,0.40812220898457224,1.1612318256507255,-0.6009056157305765,-0.027135615220864884,0.34092487893147694,-0.23612279751837567,0.05874747131835095,1.33948803032991,0.17192224692178965,0.23243894669423373,-0.2965209156540818,-0.4293174447437916,-0.6865499503746867,0.48955579739415406,0.10129371423733718,0.2071877859323831,-0.02425933403103664,-0.5014815830466675,0.39077493428360577,-0.46006961660526224,-0.3206301457882988,-0.3373299956213569,0.3236893219966055,-1.2653862959652136,0.47922448763553627,-0.43462161185905845,0.4929772393309769,0.7719162003415125,1.0350349269111523,-0.7705727835896523,-0.4788653194297089,1.4161696782597564,0.5871957235638712,0.3219132040283389,0.22452920860758568,-0.12323454706222076,-0.664069808116009,-0.04976773882405519,0.4464878850268681,-0.030280495296386156,-0.5992589491805492,-0.6957389652394289,0.8542362460021299,-0.8692832214630906,0.24411735957621095,-0.38562488876357043,0.9350976362367696,-0.20509142245552106,-0.044689377645549866,-0.090615788965064,1.445847327528229],"yaxis":"y","type":"scatter"}],                        {"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}},"xaxis":{"anchor":"y","domain":[0.0,1.0],"title":{"text":"x"}},"yaxis":{"anchor":"x","domain":[0.0,1.0],"title":{"text":"y"}},"coloraxis":{"colorbar":{"title":{"text":"color"}},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]},"legend":{"tracegroupgap":0},"margin":{"t":60}},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>

In [56]:
results_svc: Dict[str, pd.DataFrame] = {}

### Ax Helper Functions

In [57]:
def evaluate_svc(parameterization: TParameterization) -> TEvaluationOutcome:
    _C = parameterization.get("C", 1.0)
    _gamma = parameterization.get("gamma", 1.0)
    X_train, X_test, y_train, y_test = train_test_split(*create_svc_data())
    svc = SVC(C=_C, gamma=_gamma).fit(X=X_train, y=y_train)
    y_pred = svc.predict(X=X_test)
    return {"accuracy": (accuracy_score(y_true=y_test, y_pred=y_pred), None)}


def create_svc_client(
    botorch_acqf_class,
    random_class=Models.SOBOL,
    random_trials: int = 3,
) -> AxClient:
    ax_client = AxClient(
        verbose_logging=False,
        random_seed=1,
        generation_strategy=create_generation_strategy(
            botorch_acqf_class=botorch_acqf_class,
            random_class=random_class,
            random_trials=random_trials,
        ),
    )
    ax_client.create_experiment(
        name="moons_dataset_svc",
        parameters=[
            {
                "name": "C",
                "type": "range",
                "bounds": [1e-9, 1e6],
                "value_type": "float",
                "log_scale": True,
            },
            {
                "name": "gamma",
                "type": "range",
                "bounds": [1e-6, 1e6],
                "value_type": "float",
                "log_scale": True,
            },
        ],
        objectives={"accuracy": ObjectiveProperties(minimize=False)},
    )
    return ax_client

### Probability of Improvement (PI)

In [58]:
ax_client = create_svc_client(botorch_acqf_class=ProbabilityOfImprovement)
for i in range(10):
    parameterization, trial_index = ax_client.get_next_trial()
    ax_client.complete_trial(
        trial_index=trial_index, raw_data=evaluate_svc(parameterization)
    )
results_svc["PI"] = ax_client.get_trials_data_frame()

[WARNING 08-11 10:42:46] ax.service.ax_client: Random seed set to 1. Note that this setting only affects the Sobol quasi-random generator and BoTorch-powered Bayesian optimization models. For the latter models, setting random seed to the same number for two optimizations will make the generated trials similar, but not exactly the same, and over time the trials will diverge more.
[INFO 08-11 10:42:46] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[RangeParameter(name='C', parameter_type=FLOAT, range=[1e-09, 1000000.0], log_scale=True), RangeParameter(name='gamma', parameter_type=FLOAT, range=[1e-06, 1000000.0], log_scale=True)], parameter_constraints=[]).
[WARNING 08-11 10:42:49] ax.service.utils.report_utils: Column reason missing for all trials. Not appending column.


In [59]:
model = cast(
    TorchModelBridge,
    not_none(ax_client.generation_strategy.model),
)
fig = interact_contour_plotly(model=model, metric_name="accuracy")
fig.update_layout(dict(width=None, autosize=True))
render_plotly_html(fig)

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="8bbc142c-8b3a-436e-adde-9f0fff1f640c" class="plotly-graph-div" style="height:450px; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("8bbc142c-8b3a-436e-adde-9f0fff1f640c")) {                    Plotly.newPlot(                        "8bbc142c-8b3a-436e-adde-9f0fff1f640c",                        [{"autocolorscale":false,"autocontour":true,"colorbar":{"len":0.875,"tickfont":{"size":8},"ticksuffix":"","x":0.45,"y":0.5},"colorscale":[[0.0,"rgb(247,252,253)"],[0.125,"rgb(229,245,249)"],[0.25,"rgb(204,236,230)"],[0.375,"rgb(153,216,201)"],[0.5,"rgb(102,194,164)"],[0.625,"rgb(65,174,118)"],[0.75,"rgb(35,139,69)"],[0.875,"rgb(0,109,44)"],[1.0,"rgb(0,68,27)"]],"contours":{"coloring":"heatmap"},"hoverinfo":"x+y+z","ncontours":25,"visible":false,"x":[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],"xaxis":"x","y":[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],"yaxis":"y","z":[[0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608],[0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391],[0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978],[0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826],[0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374],[0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166],[0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334],[0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203],[0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362],[0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559],[0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325],[0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687],[0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752],[0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146],[0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353],[0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915],[0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985],[0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785],[0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907],[0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239],[0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425],[0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739],[0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754],[0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072],[0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196],[0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605],[0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827],[0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297],[0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205],[0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394],[0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786],[0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408],[0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381],[0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963],[0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405],[0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636],[0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073],[0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011],[0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922],[0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074],[0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626],[0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515],[0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258],[0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513],[0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975],[0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322],[0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001],[0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955],[0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815],[0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121]],"zauto":true,"type":"contour"},{"autocolorscale":false,"autocontour":true,"colorbar":{"len":0.875,"tickfont":{"size":8},"ticksuffix":"","x":1,"y":0.5},"colorscale":[[0.0,"rgb(255,247,251)"],[0.14285714285714285,"rgb(236,231,242)"],[0.2857142857142857,"rgb(208,209,230)"],[0.42857142857142855,"rgb(166,189,219)"],[0.5714285714285714,"rgb(116,169,207)"],[0.7142857142857143,"rgb(54,144,192)"],[0.8571428571428571,"rgb(5,112,176)"],[1.0,"rgb(3,78,123)"]],"contours":{"coloring":"heatmap"},"hoverinfo":"x+y+z","ncontours":25,"visible":false,"x":[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],"xaxis":"x2","y":[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],"yaxis":"y2","z":[[0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134],[0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337],[0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875],[0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584],[0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833],[0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873],[0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496],[0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615],[0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948],[0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976],[0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152],[0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931],[0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088],[0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586],[0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057],[0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814],[0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846],[0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182],[0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791],[0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541],[0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915],[0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282],[0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167],[0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072],[0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023],[0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397],[0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555],[0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852],[0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027],[0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813],[0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956],[0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385],[0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265],[0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274],[0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039],[0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801],[0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017],[0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547],[0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157],[0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274],[0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351],[0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335],[0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857],[0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817],[0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244],[0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302],[0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773],[0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501],[0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758],[0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045]],"type":"contour"},{"hoverinfo":"text","legendgroup":"In-sample","marker":{"color":"black","opacity":0.5,"symbol":1},"mode":"markers","name":"In-sample","text":["Arm 0_0\u003cbr\u003eaccuracy: 0.452 (SEM: None)\u003cbr\u003eC: 3.42871e-05\u003cbr\u003egamma: 0.000601517","Arm 1_0\u003cbr\u003eaccuracy: 0.536 (SEM: None)\u003cbr\u003eC: 55.3814\u003cbr\u003egamma: 5357.65","Arm 2_0\u003cbr\u003eaccuracy: 0.804 (SEM: None)\u003cbr\u003eC: 690.339\u003cbr\u003egamma: 0.00857996","Arm 3_0\u003cbr\u003eaccuracy: 0.816 (SEM: None)\u003cbr\u003eC: 9319.74\u003cbr\u003egamma: 0.00262294","Arm 4_0\u003cbr\u003eaccuracy: 0.82 (SEM: None)\u003cbr\u003eC: 9422.61\u003cbr\u003egamma: 0.00344744","Arm 5_0\u003cbr\u003eaccuracy: 0.82 (SEM: None)\u003cbr\u003eC: 12400\u003cbr\u003egamma: 0.00644048","Arm 6_0\u003cbr\u003eaccuracy: 0.808 (SEM: None)\u003cbr\u003eC: 11469.7\u003cbr\u003egamma: 0.00712929","Arm 7_0\u003cbr\u003eaccuracy: 0.816 (SEM: None)\u003cbr\u003eC: 7436.44\u003cbr\u003egamma: 0.00124453","Arm 8_0\u003cbr\u003eaccuracy: 0.816 (SEM: None)\u003cbr\u003eC: 40394.4\u003cbr\u003egamma: 0.00133494"],"visible":false,"x":[3.428714353076635e-05,55.38136172368294,690.33938400923,9319.742944380141,9422.61363120716,12399.99246609989,11469.710556154172,7436.440673474601,40394.43106054603],"xaxis":"x","y":[3.428714353076635e-05,55.38136172368294,690.33938400923,9319.742944380141,9422.61363120716,12399.99246609989,11469.710556154172,7436.440673474601,40394.43106054603],"yaxis":"y","type":"scatter"},{"hoverinfo":"text","legendgroup":"In-sample","marker":{"color":"black","opacity":0.5,"symbol":1},"mode":"markers","name":"In-sample","showlegend":false,"text":["Arm 0_0\u003cbr\u003eaccuracy: 0.452 (SEM: None)\u003cbr\u003eC: 3.42871e-05\u003cbr\u003egamma: 0.000601517","Arm 1_0\u003cbr\u003eaccuracy: 0.536 (SEM: None)\u003cbr\u003eC: 55.3814\u003cbr\u003egamma: 5357.65","Arm 2_0\u003cbr\u003eaccuracy: 0.804 (SEM: None)\u003cbr\u003eC: 690.339\u003cbr\u003egamma: 0.00857996","Arm 3_0\u003cbr\u003eaccuracy: 0.816 (SEM: None)\u003cbr\u003eC: 9319.74\u003cbr\u003egamma: 0.00262294","Arm 4_0\u003cbr\u003eaccuracy: 0.82 (SEM: None)\u003cbr\u003eC: 9422.61\u003cbr\u003egamma: 0.00344744","Arm 5_0\u003cbr\u003eaccuracy: 0.82 (SEM: None)\u003cbr\u003eC: 12400\u003cbr\u003egamma: 0.00644048","Arm 6_0\u003cbr\u003eaccuracy: 0.808 (SEM: None)\u003cbr\u003eC: 11469.7\u003cbr\u003egamma: 0.00712929","Arm 7_0\u003cbr\u003eaccuracy: 0.816 (SEM: None)\u003cbr\u003eC: 7436.44\u003cbr\u003egamma: 0.00124453","Arm 8_0\u003cbr\u003eaccuracy: 0.816 (SEM: None)\u003cbr\u003eC: 40394.4\u003cbr\u003egamma: 0.00133494"],"visible":false,"x":[3.428714353076635e-05,55.38136172368294,690.33938400923,9319.742944380141,9422.61363120716,12399.99246609989,11469.710556154172,7436.440673474601,40394.43106054603],"xaxis":"x2","y":[3.428714353076635e-05,55.38136172368294,690.33938400923,9319.742944380141,9422.61363120716,12399.99246609989,11469.710556154172,7436.440673474601,40394.43106054603],"yaxis":"y2","type":"scatter"},{"autocolorscale":false,"autocontour":true,"colorbar":{"len":0.875,"tickfont":{"size":8},"ticksuffix":"","x":0.45,"y":0.5},"colorscale":[[0.0,"rgb(247,252,253)"],[0.125,"rgb(229,245,249)"],[0.25,"rgb(204,236,230)"],[0.375,"rgb(153,216,201)"],[0.5,"rgb(102,194,164)"],[0.625,"rgb(65,174,118)"],[0.75,"rgb(35,139,69)"],[0.875,"rgb(0,109,44)"],[1.0,"rgb(0,68,27)"]],"contours":{"coloring":"heatmap"},"hoverinfo":"x+y+z","ncontours":25,"visible":true,"x":[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],"xaxis":"x","y":[1e-06,1.757510624854793e-06,3.0888435964774785e-06,5.428675439323859e-06,9.540954763499944e-06,1.67683293681101e-05,2.94705170255181e-05,5.1794746792312125e-05,9.102981779915228e-05,0.00015998587196060574,0.0002811768697974231,0.0004941713361323833,0.000868511373751352,0.0015264179671752333,0.0026826957952797246,0.004714866363457394,0.008286427728546842,0.014563484775012445,0.025595479226995333,0.04498432668969444,0.07906043210907701,0.1389495494373136,0.244205309454865,0.42919342601287785,0.7543120063354607,1.325711365590108,2.329951810515372,4.094915062380427,7.196856730011514,12.648552168552959,22.229964825261955,39.06939937054613,68.66488450042998,120.67926406393264,212.09508879201925,372.7593720314938,655.1285568595496,1151.3953993264481,2023.5896477251556,3556.4803062231213,6250.551925273976,10985.411419875572,19306.977288832455,33932.217718953296,59636.23316594637,104811.3134154683,184206.99693267164,323745.754281764,568986.6029018281,1000000.0],"yaxis":"y","z":[[0.44356211245639093,0.44145510641767405,0.4397124084771437,0.4383856244660861,0.4375281042215909,0.4371942775592792,0.4374388212293931,0.4383156442188362,0.43987668602204655,0.44217053398973577,0.4452408823615758,0.4491248771840477,0.4538514166799558,0.45943950228412267,0.46589675556980775,0.4732182232321127,0.48138557978866253,0.490366803929847,0.5001163548332744,0.5105758208666457,0.5216749683577385,0.5333330921018006,0.5454605644884766,0.5579604925284258,0.570730414275556,0.5836639908250008,0.596652671843845,0.6095873284653768,0.6223598562347304,0.6348647526824222,0.6470006696856165,0.6586719310752813,0.6697899923358658,0.6802748036098392,0.6900560221585129,0.6990740093276737,0.7072805438784346,0.714639192095982,0.721125297809415,0.7267255917156484,0.7314374640632857,0.7352679879476646,0.7382328096183558,0.7403550265043425,0.7416641495289135,0.7421952006058776,0.7419879445982838,0.7410862150372367,0.7395372759560787,0.737391169147833],[0.44035889816806517,0.43812252784846883,0.43625748603630965,0.4348179008032389,0.43385997810674287,0.43344134256349215,0.4336201950456623,0.43445426869418163,0.4359995712655206,0.43830891292070445,0.44143023611235277,0.4454047890998474,0.45026521625857197,0.45603367324943767,0.46272010573447964,0.47032084557884773,0.4788176672799241,0.48817740484011646,0.4983521621864869,0.5092800763984909,0.5208865336003285,0.5330857066586211,0.5457822837854058,0.5588732796674001,0.5722498538937992,0.5857990949380981,0.5994057554013206,0.6129539429345712,0.6263287808439433,0.6394180535316183,0.652113845660251,0.6643141713342948,0.6759245719521916,0.6868596405020684,0.697044408702423,0.7064155155562687,0.7149220668809724,0.7225261010575512,0.7292026013992188,0.7349390413003037,0.7397345093386711,0.7435985244530888,0.7465496969475889,0.7486144009386763,0.7498255899934588,0.7502218196633166,0.7498464635666011,0.7487470524910631,0.7469746464335997,0.7445831666537271],[0.43733011950293416,0.4349679088469291,0.4329832125502215,0.43143256193596335,0.43037490886264024,0.42987097972038785,0.42998243401674596,0.4307708029737075,0.4322961882826139,0.4346157111203151,0.4377817190340652,0.4418397856251997,0.44682657608060683,0.45276769796126975,0.45967570248361617,0.4675484308464903,0.47636789394627777,0.48609982067558644,0.49669391766631144,0.5080847799920691,0.5201933124923411,0.532928486465587,0.5461892661205849,0.559866577478261,0.5738452403392704,0.5880058277224847,0.6022264502225629,0.616384483561348,0.6303582672143982,0.6440288019920607,0.6572814662202467,0.6700077547071119,0.6821070229282665,0.6934881922226688,0.704071342849818,0.7137890949767937,0.7225876597581108,0.7304274421751242,0.7372831026799918,0.7431430406280713,0.7480083448829342,0.7518913488690345,0.7548139997173003,0.7568062724248837,0.7579048130580143,0.7581518924501397,0.7575946348464431,0.7562844032801878,0.7542762032639178,0.7516280028678008],[0.4345027228735361,0.4320200765115368,0.4299203093591274,0.42826220384942704,0.4271073059271893,0.426519300160184,0.4265631798478158,0.4273041814086212,0.42880645482320806,0.4311314495312676,0.4343360110498581,0.43847021158957755,0.4435749816073031,0.4496796686611358,0.4567997167052668,0.46493471145707993,0.47406704374329384,0.4841613777907156,0.49516498195993336,0.5070088311532845,0.5196092815351457,0.5328700818116492,0.5466845135812294,0.5609375155918446,0.5755077136111761,0.5902693322605487,0.6050940025703267,0.6198525004670656,0.6344164600121749,0.6486601036753277,0.6624620218666339,0.6757070160562921,0.6882879943421624,0.7001078758837088,0.7110814231336092,0.7211368826916623,0.7302172848364764,0.7382812400680453,0.7453030920785358,0.7512723514919118,0.756192443713378,0.7600789378297339,0.7629575393029442,0.7648621734189837,0.7658334231998706,0.7659174288645183,0.7651651747367003,0.7636319685919567,0.7613769032174947,0.758462162506296],[0.4319030899352518,0.4293073892074243,0.4270991552732322,0.42533923969853477,0.42409159135187946,0.4234226591665728,0.4234005834396956,0.42409413937651047,0.4255713964125167,0.4278980610913038,0.4311354835832803,0.4353383337967994,0.4405519993843079,0.4468098300987409,0.45413044665398267,0.4625154216717379,0.4719476738142373,0.482390840975059,0.49378971300396035,0.5060715853659937,0.5191482461072688,0.5329182786839086,0.5472694259194731,0.562080857822971,0.5772252750621877,0.5925708437715337,0.6079829962464197,0.6233261518744824,0.638465419097948,0.6532683359439588,0.6676066952899016,0.6813584816309597,0.6944099179624502,0.7066575838209901,0.7180105191681887,0.7283921772328563,0.7377420411682447,0.7460166893550589,0.7531901030559407,0.7592530791288785,0.7642117497862243,0.7680854032396224,0.7709039849277356,0.7727057486722615,0.7735354461429782,0.7734432007397736,0.7724839249355919,0.7707169610846587,0.7682056294696299,0.7650165065907649],[0.429556467668892,0.4268571102475899,0.4245491030283398,0.42269516018749953,0.4213614079311587,0.4206168192753539,0.4205324341359153,0.42118032394870286,0.42263225711362773,0.4249580217733406,0.42822336938533556,0.43248756267726934,0.4378005552939261,0.4441999109123105,0.4517076936718473,0.4603277069116829,0.4700435460992254,0.48081785592009413,0.4925929099030482,0.5052922955503314,0.5188232829043735,0.5330794516217976,0.5479432756428799,0.5632885098163763,0.5789823335694027,0.5948872745326669,0.6108629706452567,0.6267678447188002,0.6424607687725259,0.6578027906758989,0.6726589838937385,0.6869004616578076,0.700406567759936,0.7130672150723933,0.7247852884318929,0.735478962250314,0.7450837128150799,0.75355374795891,0.7608625611434218,0.7670023789002142,0.7719824387947579,0.7758263038766784,0.7785687162264663,0.7802526704428938,0.7809272958030017,0.7806467564799876,0.7794699121520527,0.7774602128379348,0.7746853574985749,0.7712165076337342],[0.42748636015133623,0.424694729512416,0.4222977265830509,0.4203597039434391,0.41894871252499344,0.41813597000342695,0.41799511411495244,0.4186011970495716,0.42002937176610505,0.4223532173248268,0.42564265097858656,0.42996138587475446,0.43536392705128246,0.4418921765656289,0.4495718679732401,0.45840927132080783,0.4683888049809097,0.47947214579596265,0.4915990219703568,0.5046893370428736,0.518645995097164,0.5333578695151118,0.5487025846720752,0.5645489813636775,0.580759260116124,0.5971908584273643,0.6136981446912736,0.6301340205203819,0.6463515231746539,0.6622055142242566,0.6775545297326648,0.6922628494792034,0.7062028149238718,0.719257383628295,0.7313228475590636,0.7423115622415739,0.7521544376984074,0.7608028476884949,0.7682295566696966,0.7744282985376408,0.779411826326965,0.7832086128471178,0.7858588470064867,0.7874107178556773,0.787917905299943,0.7874385970561573,0.7860355677188814,0.7837764484528686,0.7807334994311489,0.7769826813054694],[0.4257139038319208,0.4228432569144799,0.4203700247789355,0.41835996410570275,0.4168827799713492,0.4160116264752907,0.4158223938962955,0.4163927368930794,0.4178007912982505,0.4201235202014906,0.42343462490247463,0.42780195715873365,0.43328438664746066,0.43992813716356755,0.44776275759027995,0.4567971966476175,0.4670168340140146,0.47838239574967056,0.4908310610883336,0.5042791651161279,0.518625546056931,0.5337548398799236,0.5495404073066233,0.5658468249540761,0.5825319863924597,0.5994489025309286,0.616447304460224,0.6333751539825565,0.6500801645184047,0.6664114298020675,0.6822212491607823,0.6973672238857386,0.7117146752438842,0.725139395272486,0.7375306794608866,0.7487944989992803,0.7588565479543538,0.7676647603745245,0.7751907733825675,0.7814297891248534,0.786398461143019,0.7901308823958426,0.7926734527488013,0.7940800615494846,0.7944090597461433,0.7937225477915585,0.7920871429558196,0.7895747672337713,0.7862624827207175,0.7822312802382161],[0.4242572538719812,0.42132251932560755,0.4187876171119816,0.4167194706985515,0.4151891600195546,0.4142714502903662,0.4140441098641773,0.41458697109093706,0.4159806803213864,0.41830507455596916,0.42163711329415954,0.426048286718287,0.4316014214303437,0.4383468320634228,0.44631788124331145,0.4555263527809819,0.4659587116086211,0.4775747468503121,0.4903091488140665,0.5040749573675308,0.5187674510328485,0.5342676971053476,0.5504455459046315,0.5671620919623169,0.5842716992816772,0.6016237055795852,0.6190639217163136,0.6364360397067488,0.6535830591881711,0.670348838327745,0.6865798697255076,0.7021273723980808,0.7168497731176557,0.7306156174091024,0.7433068924016254,0.7548226479307648,0.7650826578092504,0.7740306720984416,0.7816366093847368,0.7878969175667878,0.792832442465506,0.79648365220842,0.7989040505523928,0.8001537999850494,0.8002959716509999,0.7993963640230287,0.7975253666362673,0.7947594001419093,0.7911806491705183,0.7868753465236034],[0.42313101357554006,0.4201484990725754,0.4175679766446687,0.415457301426623,0.4138886477991525,0.41293806041332176,0.4126847966744676,0.41321041465237884,0.41459755229038836,0.416928334485666,0.42028233405877985,0.424734001071541,0.4303494638842485,0.4371826020336629,0.4452703320445299,0.45462730592607503,0.4652411708791397,0.4770708108363538,0.49004863504275104,0.5040849184521689,0.5190721442079611,0.534888680816119,0.5514017613650737,0.5684698750364172,0.5859447011667904,0.6036727132727091,0.621496574714558,0.6392564429840518,0.6567912965041647,0.6739403958766714,0.6905449895428117,0.7064503696775349,0.7215083739239169,0.7355804054214262,0.7485409958722221,0.7602818461351757,0.7707161229242867,0.7797825513202348,0.787448539886331,0.7937113111394417,0.7985959958986113,0.8021501491353726,0.8044353858123331,0.805518798043217,0.8054681413130488,0.8043526160625212,0.8022464170427598,0.7992308537049905,0.7953936140553535,0.7908262643161258],[0.42234574114271467,0.41933275596282205,0.4167237514514727,0.4145872836518658,0.41299634398584806,0.4120279254629806,0.4117623820182417,0.41228253506818774,0.4136724732434078,0.41601598184309746,0.41939452768442576,0.4238847124961096,0.4295550937040868,0.43646225577672654,0.4446460036478474,0.45412361440110904,0.4648839538556128,0.47688512214049505,0.4900577709092756,0.5043102999329108,0.5195334185714491,0.5356038181894012,0.5523870896167369,0.5697400360483624,0.587512521334725,0.6055489836320068,0.623689737043151,0.6417721792546791,0.6596320209982037,0.6771046529852461,0.6940267669854707,0.7102383484475941,0.7255851555779147,0.7399217883224035,0.7531154189972684,0.7650501834586655,0.77563208269652,0.78479397403575,0.792499816663352,0.798746870047584,0.8035643281614346,0.8070073190355981,0.8091465821002349,0.8100568797297286,0.8098105450091515,0.8084799242807788,0.8061433513012188,0.8028876504915435,0.7988063123810887,0.7939960067681845],[0.4219075670185115,0.4188819746389178,0.4162622273163633,0.41411735426271384,0.4125208892518029,0.4115504446229568,0.411287079068382,0.4118144133187861,0.41321743970421715,0.4155809621456023,0.4189875922387665,0.42351521451159796,0.42923381942184796,0.43620158593875896,0.4444600763025449,0.4540283843195019,0.4648964473325901,0.4770220281525193,0.49033507960372635,0.5047433553430895,0.5201369679197909,0.5363920124232506,0.553373426889832,0.5709372432080848,0.5889323684650615,0.6072020262888181,0.6255849805274551,0.6439166593529413,0.6620302963836932,0.6797582064294027,0.6969333165652243,0.7133910776383375,0.7289718852791174,0.7435241392046551,0.7569080564497838,0.7690003089539936,0.77969943797662,0.7889317314852113,0.7966567383697017,0.802870844215137,0.8076067594907261,0.8109271982695134,0.8129126989852589,0.8136464198312685,0.8132052059120397,0.8116647146152961,0.8091083186530132,0.8056290588153585,0.8013260703923965,0.7963003006264373],[0.4218179504535048,0.41879767392929684,0.4161849790322551,0.41404913908546576,0.4124639539578842,0.4115073243970435,0.4112606197375772,0.411807792981134,0.41323418908316883,0.4156249828349958,0.4190631718069731,0.4236270372059928,0.4293869709546783,0.436401550554361,0.4447127241897928,0.45433995446637904,0.4652736764936174,0.47747243242303056,0.49086695954223064,0.5053657146205178,0.5208594102879296,0.5372246134280487,0.5543265746588439,0.5720214420605788,0.5901579985966913,0.608579052339889,0.6271226014969553,0.6456228921531524,0.6639114854914862,0.6818184528583555,0.6991738212885821,0.7158093986756786,0.731561115979125,0.746272031911181,0.7597961487218734,0.7720031733391673,0.7827842921799278,0.7920588230206554,0.7997810746590078,0.8059456594989777,0.8105881957787036,0.8137785394944349,0.8156066754779223,0.8161643528263661,0.8155333255181454,0.8137940305077463,0.8110363051380651,0.8073594589144779,0.802867091280068,0.7976628569460126],[0.4220735956048114,0.41907610465818784,0.41648774511360453,0.41437779817324627,0.41282004558661783,0.41189233678185855,0.4116759479032343,0.41225468649324126,0.4137136873633916,0.4161378357221445,0.4196097427048475,0.4242071859425091,0.42999991380451885,0.43704569797002407,0.4453855174573023,0.45503788065011713,0.46599324965096833,0.47821184387933285,0.4916265584382379,0.506147859353026,0.521668226932641,0.5380657416102855,0.5552069062114202,0.5729488469581019,0.5911410304154435,0.6096266247955207,0.6282436272941272,0.6468258752184946,0.6652040576445807,0.6832068461954736,0.7006622682292807,0.7173994532321168,0.7332508934169484,0.7480553720102935,0.7616617259999322,0.7739336192563876,0.7847554897151182,0.794039739042315,0.8017348412629087,0.807832789373698,0.8123717463537693,0.8154286018188293,0.8171013695799173,0.8174886438442226,0.816678982908204,0.8147610293869596,0.8118317957547111,0.8079950494441779,0.8033565043843505,0.7980205175701462],[0.4226665363660785,0.4197083480840792,0.4171605422293745,0.4150921591216436,0.41357666447485614,0.41269150180165576,0.41251743428065635,0.4131376295123381,0.4146364324359005,0.4170977623743775,0.4206030597832569,0.4252286973873757,0.4310427615962151,0.4381011143095712,0.44644270926063473,0.45608443742381155,0.46701665638154666,0.47920149934451944,0.4925748276721669,0.5070501829028753,0.5225228793112572,0.5388735021063635,0.5559707146505328,0.5736734593548012,0.5918326728972243,0.610292639026309,0.6288920988887851,0.6474652360544108,0.6658426528413728,0.6838524566265956,0.7013215797089852,0.7180774640743921,0.7339502531898383,0.7487756468355731,0.7623985919650007,0.7746780020806248,0.785492716233499,0.7947489081988393,0.8023890274916534,0.8084014557835355,0.8128263108080679,0.8157479925436559,0.8172725189661589,0.8175035388306041,0.816538441109464,0.8144763386151102,0.8114194693319889,0.8074727125278608,0.8027413218059891,0.7973286043002024],[0.42358438653742014,0.4206806107448007,0.4181880140373338,0.41617513161841935,0.41471479902826813,0.4138836827259778,0.4137615970877572,0.414430561167326,0.41597354078880067,0.41847281314120816,0.42200788282908114,0.4266528728237749,0.4324733185362399,0.4395223306952952,0.4478362231611397,0.4574300412501006,0.46829400003491006,0.480392121958786,0.49366352833970695,0.5080254949422291,0.5233770009098939,0.5396019999885927,0.556572153673459,0.5741490165948595,0.592185754364805,0.610528500888407,0.6290174685411141,0.6474879257872916,0.6657711579290777,0.683695529526387,0.7010877722964193,0.7177746302936496,0.7335850051008999,0.7483527578525727,0.7619203424500655,0.7741434656992384,0.7848969957668757,0.7940823704295832,0.8016367838001416,0.8075442658988625,0.8118454501127389,0.8146315316774911,0.8160181931035163,0.8161193670198158,0.8150404047152231,0.8128850747190616,0.8097566486797745,0.8057587086837688,0.8009944837732849,0.7955651787702914],[0.4248107396869994,0.42197469554761646,0.41954998813058747,0.41760436847252375,0.4162097137303689,0.4154415300721534,0.41537823910972477,0.41610020186935104,0.4176884275678763,0.420222908219312,0.4237805163468441,0.4284324067219352,0.43424088566829167,0.4412557782243598,0.4495104783523177,0.45901814655773954,0.4697688350245012,0.48172834358478694,0.4948390638521968,0.5090223024076789,0.5241812397859302,0.5402038642973813,0.5569655500939518,0.574331185628766,0.5921568796702218,0.6102913241486205,0.6285769137208873,0.6468507302998705,0.6649455054882084,0.6826906785438017,0.6999136737659472,0.7164415297687771,0.732103024429384,0.7467314537264558,0.7601682406712035,0.7722675727787727,0.7829022943144917,0.7919713155869899,0.7994088525743989,0.8051958934699244,0.8093725814460363,0.8120342553604889,0.8133051351270657,0.8133135144280019,0.8121720617945535,0.8099811590891719,0.806841258454553,0.8028532908795619,0.7981176664940012,0.7927328385013269],[0.42632569280542376,0.4235686158971657,0.4212221980918175,0.4193531168066029,0.41803195527788717,0.41733267401990576,0.4173318641916216,0.4181077387458003,0.4197388123726048,0.422302218407731,0.4258716131805044,0.4305146320853894,0.43628989896136516,0.44324367040010115,0.4514063393434735,0.4607892181775234,0.4713821769820538,0.48315265225440873,0.49604618185410554,0.5099881589433042,0.5248862432025159,0.5406329094615498,0.5571078049620574,0.5741797717030268,0.5917085131836404,0.6095459524294168,0.6275373621381137,0.6455223648330606,0.6633359107744581,0.6808093491003984,0.6977717157857651,0.7140513718356454,0.7294781374643899,0.7438860835204645,0.7571171609489414,0.769025874061112,0.7794852365471455,0.7883942961117043,0.7956875829669545,0.801346821386106,0.805412315479422,0.8079795101397885,0.8091763594024171,0.8091372951054525,0.8079802742711524,0.805805515252843,0.8027093315228334,0.7987884910529095,0.7941395440644606,0.7888574026859472],[0.42810646084967274,0.4254373112121551,0.42317711757214105,0.42139119127589547,0.42014848876577937,0.41952105065036754,0.4195832233458281,0.42041062251901085,0.42207879521119196,0.42466153871931184,0.42822884273364553,0.4328444431547347,0.43856302087111854,0.44542715714745523,0.45346427172989917,0.46268389542755084,0.4730756965428409,0.4846086025553375,0.49723111684860555,0.5108726365474043,0.5254453913776199,0.5408466094522902,0.5569606184914699,0.5736607219773167,0.5908107967232121,0.6082666293952885,0.625877052052628,0.6434849615992673,0.6609283235818934,0.6780412723711868,0.694655430572338,0.7106015823682384,0.7257118496217285,0.7398225369989642,0.7527778343638376,0.7644345929067901,0.7746684273368404,0.7833814333294058,0.7905117693993561,0.7960446493208464,0.8000206319724673,0.8025316763512877,0.803702336636406,0.8036649200798667,0.802538897639061,0.8004268077919865,0.7974230537119364,0.7936202342870986,0.7891103626288538,0.7839840640548255],[0.4301280460675463,0.42755341897768034,0.4253848505247807,0.42368599959797953,0.4225238769288277,0.42196825378170266,0.42209085691404913,0.42296431375990473,0.4246608121870261,0.42725044424204395,0.4307992165593569,0.4353667366161241,0.4410036296012177,0.4477488087767283,0.45562680676070877,0.46464545120850426,0.4747941910366519,0.48604330640844845,0.4983440695743442,0.5116297296442487,0.5258170592968746,0.5408081688837441,0.556492344648162,0.5727477553078344,0.5894429565383887,0.6064381890082898,0.6235865112100553,0.6407348384743141,0.6577249801294328,0.6743947824402743,0.6905794989231676,0.7061135239867686,0.720832642002154,0.7345769628484936,0.747194737116017,0.758547267690076,0.7685151481338844,0.777006011178707,0.7839636598048634,0.7893772656665631,0.7932865931628234,0.7957774360064682,0.7969659107572082,0.7969773893615908,0.7959292182546401,0.7939249671000059,0.7910585105265956,0.7874194063670223,0.7830953715116062,0.7781724902827989],[0.43236392643742155,0.42988806009957,0.4278140253060083,0.42620355745974103,0.4251214273475023,0.42463482411244174,0.42481253148632747,0.42572386692010167,0.427437356197621,0.4300191242465141,0.4335309990641101,0.43802835334063994,0.443557750127589,0.4501545138441735,0.4578404072488204,0.4666216388327696,0.47648742606829647,0.4874092783055607,0.4993410463454083,0.5122196532718923,0.5259663227403595,0.5404880854006523,0.555679367126345,0.5714235193511183,0.5875942164726334,0.6040567024128216,0.6206689128179619,0.6372825320332128,0.6537440681935626,0.6698960489620535,0.6855784573402429,0.7006305434456209,0.7148931651994275,0.72821182832149,0.7404406111217422,0.7514471623535669,0.7611189201028621,0.7693705294209849,0.7761519296802464,0.7814554414766608,0.7853186136228545,0.787819375202137,0.789063084956768,0.7891656332732921,0.7882392601618796,0.7863861342114926,0.783699194696234,0.7802656280622103,0.7761694328278751,0.7714923445597938],[0.43478673096482146,0.43241159962399855,0.4304326484117268,0.42890944190170915,0.4279042501968596,0.42748141283496255,0.4277065060188688,0.4286452889224872,0.43036240980776347,0.43291986279980804,0.43637520346468534,0.44077955765593296,0.44617549386001604,0.4525948715051367,0.4600568179210296,0.4685660105022933,0.4781114319914663,0.4886657168120759,0.5001851226660059,0.5126100687357016,0.5258661095772663,0.5398651812592397,0.554506964381253,0.5696802446009157,0.5852641990202321,0.6011295840182368,0.6171398407695595,0.6331521674545346,0.6490186332960769,0.6645874311071316,0.6797043838532263,0.6942148379308002,0.707966091285264,0.7208105157005021,0.7326095322673067,0.7432385689093954,0.752593027131275,0.7605950282242205,0.7672001749387931,0.7724027195069156,0.7762367806714373,0.778771619680396,0.7801011229581676,0.7803305059447265,0.7795647793863496,0.7779023548745168,0.77543392169854,0.7722441336516802,0.7684135869598901,0.7640199629079326],[0.43736887497834714,0.4350943524093784,0.43320888399356844,0.43176964641133336,0.43083618804650264,0.4304697816504002,0.43073259291295696,0.43168664672149704,0.433392579261745,0.4359081751506986,0.4392867057445432,0.443575108301562,0.4488120749416231,0.45502615177750166,0.4622339751572222,0.47043878383310395,0.47962933371249855,0.489779302031759,0.5008472067247479,0.5127768001800239,0.5254978430207162,0.5389271358152926,0.5529696872420304,0.5675199199116723,0.5824628498665965,0.5976752138509684,0.6130265542076276,0.6283803023944102,0.6435949284813711,0.6585252463913804,0.6730239838475545,0.6869437419448505,0.7001394802155294,0.7124716640545364,0.7238101914484136,0.7340391533100517,0.7430623377794414,0.7508091093299474,0.757239842481008,0.76234955492544,0.7661681154321994,0.7687559260078353,0.770195467358449,0.7705808730814149,0.7700085805721362,0.7685713660261294,0.7663561601809572,0.7634443807640929,0.7599131263020973,0.7558361701680248],[0.4400831349615126,0.43790721170708274,0.4361117361258876,0.4347513147394039,0.43388259637119436,0.4335636217832933,0.4338530035878857,0.43480892377175645,0.4364879432976688,0.43894362934400216,0.44222502142246956,0.4463749777741187,0.4514284666488799,0.4574108899548781,0.46433654390280055,0.47220732614567756,0.4810117861887157,0.4907245843625973,0.5013063794290656,0.5127041162831028,0.5248516451422734,0.5376705808041623,0.551071307732459,0.5649540509776765,0.5792099582691093,0.5937221688627593,0.6083668753151309,0.6230144127167686,0.6375304350726336,0.6517772602313899,0.6656154827243259,0.6789059668000132,0.6915123365647358,0.7033040697480436,0.7141602640220931,0.72397406028696,0.7326575493233031,0.7401467345282907,0.7464057906120259,0.7514295596318136,0.7552432014564578,0.7578984191879884,0.7594667042421407,0.7600311457625368,0.7596788604650268,0.7584956471649659,0.7565633315982638,0.753959193238688,0.7507564363556689,0.7470248607670156],[0.4429031489888047,0.44082218674026846,0.43911162075915144,0.43782334239511317,0.43701096731154804,0.43672919005030003,0.4370329842683479,0.43797664082887977,0.4396126432731485,0.44199039075381114,0.4451547924272489,0.44914477405490155,0.4539917555720035,0.45971817477386717,0.4663361430544451,0.4738463200523311,0.48223708211849514,0.49148403467533663,0.5015498846069759,0.512384652787723,0.5239261765997077,0.5361008338592792,0.5488244154155075,0.5620030826007382,0.5755343641566497,0.5893081710430992,0.6032078331000377,0.6171111864441339,0.6308917633007496,0.6444201557239373,0.6575656401255643,0.6701981584514863,0.6821907499601911,0.6934225076277994,0.7037820841587338,0.7131716800354039,0.7215112967210159,0.728742832573657,0.7348333749304895,0.7397768975224822,0.7435936554810881,0.7463269913665019,0.7480379637919653,0.748798898189541,0.7486872636982876,0.7477810085506821,0.7461557980099667,0.7438838997523471,0.7410340906623085,0.7376719685082916],[0.44580383488283876,0.44381284256172426,0.4421808226629541,0.44095684423064346,0.4401913994886631,0.43993577057177424,0.44024125767153816,0.44115826481011017,0.4427352466172741,0.44501752913334436,0.448046029654476,0.45185591426219934,0.4564752454462544,0.46192368383159854,0.4682113145936965,0.47533766794353094,0.48329099244123785,0.49204782027251054,0.5015728378719811,0.5118190482051056,0.5227281879668606,0.5342313481736116,0.5462497421558417,0.5586955704605681,0.5714729455677071,0.5844788578053945,0.5976041847215241,0.6107347672852518,0.6237525960384723,0.6365371672670689,0.6489670816215302,0.660921962559865,0.6722847649778032,0.6829445187173467,0.6927994986561725,0.7017607242024491,0.7097555631261442,0.7167310600577642,0.7226564688907945,0.7275244136522002,0.7313502190106008,0.734169280538701,0.7360328196163942,0.7370028055359349,0.7371470160028473,0.7365350455466263,0.7352356496437069,0.7333153545736238,0.7308379711356345,0.7278645865838299],[0.44876172340029763,0.44685464136725433,0.4452938391709497,0.4441254934432949,0.44339692364943434,0.4431559772287197,0.44345029168470107,0.4443264330539432,0.44582891689953996,0.44799912654203405,0.45087415335913034,0.4544855949013147,0.45885835698786254,0.4640095140784829,0.46994728604008146,0.47667018718593834,0.48416639428997305,0.49241336473731806,0.5013777162251483,0.5110153588362141,0.5212718525681403,0.532082951541076,0.5433752917612524,0.5550671825455007,0.5670694713093587,0.5792864655066445,0.5916169120701585,0.6039550519258363,0.6161917834479789,0.6282159825029077,0.6399160359924299,0.6511816476529451,0.661905965068717,0.671988049844399,0.6813356625860331,0.689868256700929,0.6975199727469622,0.7042423141739869,0.7100061003723261,0.7148022840470148,0.7186413338254518,0.7215511296595317,0.7235736422003007,0.7247609519247965,0.725171286702596,0.7248656621924738,0.723905448772758,0.7223508877562663,0.7202603604606076,0.7176901294339543],[0.4517552079227672,0.449925188951854,0.4484276172432693,0.44730574198300493,0.44660369820766965,0.4463659154807352,0.44663641843144386,0.4474580210540609,0.44887142278431114,0.4509142218172422,0.45361986953753686,0.4570165985882301,0.4611263649323511,0.465963849910746,0.4715355703566145,0.47783914217434953,0.4848627350012329,0.4925847432174728,0.5009736832745928,0.5099883114617064,0.5195779424221371,0.5296829391434544,0.5402353410503367,0.5511595984475489,0.5623733881940611,0.5737884958676662,0.5853117623088835,0.5968461058348431,0.6082916441710392,0.6195469507695484,0.6305104868117452,0.6410822502724776,0.651165673448366,0.6606697760436979,0.6695115382117874,0.6776183953699624,0.6849306789076434,0.6914037491445552,0.6970095159124086,0.7017370513873964,0.7055920950236422,0.7085954299253091,0.7107803317595318,0.7121894814522336,0.7128718182159173,0.7128797574929706,0.7122670373228354,0.7110872587028738,0.7093930254371069,0.7072355073963125],[0.4547647152633988,0.45300439320560554,0.4515616934848853,0.45047693517328136,0.44979109100273956,0.44954522357483173,0.4497798274476353,0.4505340808154028,0.4518450159541969,0.45374662398059684,0.4562689163801755,0.4594369725783557,0.46327000868437446,0.4677805064299359,0.47297344226710847,0.47884565387860445,0.4853853748068503,0.4925719580433616,0.5003757974536991,0.5087584435599324,0.5176728993082136,0.5270640735836383,0.5368693663729287,0.5470193598673065,0.5574385940314696,0.5680464123653948,0.578757872648781,0.5894847272244087,0.6001364867021071,0.6106215886553619,0.6208486975188314,0.6307281615911683,0.6401736452625634,0.6491039362281515,0.6574448956410981,0.665131473057059,0.6721096516450273,0.6783381341795747,0.6837895465419188,0.6884509459006811,0.6923234912150127,0.6954212603493609,0.6977693512866238,0.6994015366667757,0.700357805188953,0.7006820992973487,0.7004204608692531,0.699619667222801,0.6983263250795535,0.6965863198934256],[0.4577728043870706,0.45607454363057964,0.4546782485940156,0.453621334766734,0.45294166440222444,0.45267701319877046,0.4528644558064296,0.45353967515417903,0.4547362053811435,0.4564846235499303,0.45881171095758444,0.46173961020571763,0.4652850085651685,0.46945838082547325,0.4742633250769204,0.4796960222893829,0.485744845078446,0.49239013312609153,0.4996041432630412,0.5073511724614581,0.5155878432504598,0.5242635344840398,0.5333209366883287,0.5426967106126056,0.552322229845105,0.5621243928091918,0.5720264953096897,0.5819491611845056,0.5918113347099917,0.601531343445883,0.611028043407793,0.6202220588534905,0.6290371251629711,0.6374015332641126,0.6452496553650203,0.652523502617337,0.659174226916023,0.6651634383269279,0.6704641806783197,0.6750614085395735,0.6789518524229421,0.6821432444701351,0.6846529842700091,0.686506420978934,0.6877349818896307,0.6883743731624874,0.6884630223412518,0.6880408490375247,0.6871483692326571,0.6858260815674916],[0.46076420121577444,0.4591203220280333,0.45776208855782513,0.45672406504740765,0.4560410806929765,0.4557477287830336,0.4558777964689307,0.45646363100589016,0.45753545245786154,0.45912062738779275,0.46124292263321737,0.4639217624522563,0.46717151558799425,0.4710008405902402,0.47541211758350316,0.4804009923020062,0.48595605364354705,0.4920586595861493,0.49868291874693005,0.5057958270393106,0.5133575517473266,0.5213218496943476,0.5296366025631176,0.5382444509883093,0.5470835096018731,0.5560881473013624,0.5651898200187532,0.5743179465669759,0.5834008212268527,0.5923665593196973,0.6011440740550311,0.6096640845725664,0.6178601562644201,0.6256697743241939,0.6330354476744237,0.6399058290834688,0.6462368148076396,0.6519925543135044,0.6571462668893235,0.661680744379778,0.6655884345832705,0.6688710528730676,0.6715387475653732,0.673608922061727,0.6751048681355523,0.6760543755427426,0.6764884551958824,0.6764402611721388,0.6759442403029241,0.6750354929457949],[0.46372577840384366,0.46212875496303124,0.4608005650262995,0.45977299627551066,0.45907794388681306,0.45874694329327903,0.4588106442280224,0.4592982323924685,0.4602368086670685,0.4616507395625019,0.4635609963175993,0.46598450332568725,0.4689335190052338,0.4724150734201282,0.47643048657408893,0.4809749891809461,0.4860374638936287,0.49160031974881385,0.4976395064594714,0.504124668813241,0.5110194354843701,0.5182818316127735,0.5258648009103736,0.5337168209226721,0.5417825942384824,0.5500037985322758,0.5583198788650817,0.5666688662168462,0.5749882065273276,0.5832155847195041,0.5912897289614327,0.5991511830889023,0.606743041246738,0.614011649224802,0.6209072897697692,0.6273848778091138,0.6334046855790312,0.6389330890151245,0.6439432796669995,0.6484158414988762,0.6523390760698896,0.6557089869670486,0.6585288962938557,0.660808737464621,0.6625641235583228,0.663815314051262,0.6645861940774888,0.6649033492764678,0.664795279795539,0.6642917614482738],[0.4666464891665157,0.4650891185449322,0.46378344689667594,0.4627585789879091,0.4620435928650292,0.461667106721715,0.461656796567292,0.462038871290043,0.4628375147614852,0.4640743077729014,0.46576764559535927,0.46793216951965655,0.47057823254896863,0.4737114201878344,0.4773321467695372,0.4814353458834334,0.4860102702582799,0.49104041215309885,0.4965035502789663,0.5023719239907427,0.5086125304230287,0.5151875357957925,0.5220547885220947,0.5291684190550692,0.5364795094539578,0.543936814110503,0.5514875115647153,0.5590779655174063,0.5666544709270777,0.5741639588787184,0.5815546329870297,0.5887765128382919,0.5957818698506944,0.602525561311082,0.6089652992393937,0.6150619236706165,0.6207797652768761,0.6260871573649806,0.6309570877243336,0.6353678957049048,0.639303866852196,0.6427555853531439,0.6457199640719021,0.6481999496090444,0.6502039638541707,0.651745177810943,0.6528407173690843,0.6535108827273926,0.6537784348568655,0.6536679738599527],[0.46951726406086663,0.4679928056201877,0.46670275440045084,0.4656736415992261,0.4649318593748482,0.4645032617388049,0.4644127247010348,0.46468367231921137,0.46533757789924896,0.46639345220490236,0.46786733296077,0.4697717919440138,0.47211547731446146,0.47490270931157086,0.478133146889914,0.4818015412061002,0.4858975891603354,0.49040589660809764,0.495306056666308,0.5005728440772228,0.506176522194246,0.5120832550836993,0.5182556136425678,0.5246531615083321,0.5312331037211495,0.5379509783019643,0.5447613677863732,0.5516186040153022,0.5584774350874213,0.5652936188252795,0.5720244038995574,0.5786288610211164,0.5850680376399211,0.5913049373244307,0.597304374185681,0.6030328163302587,0.6084583801643157,0.6135511217403984,0.6182836681344104,0.6226320850180085,0.6265767751710846,0.6301031997241339,0.6332022887626745,0.6358705048076799,0.6381095994947841,0.6399261457413882,0.6413309380815928,0.6423383428221486,0.6429656579789618,0.6432325192225317],[0.47233087916068334,0.47083316478097187,0.4695525660321017,0.468513162521283,0.467738802889194,0.4672527392043961,0.4670772280671863,0.46723310499243226,0.4677393408417158,0.46861259123899696,0.46986675186687865,0.4715125341180842,0.4735570765835898,0.47600360813188064,0.47885117775874525,0.4820944649211275,0.48572368175518293,0.48972457554693727,0.4940785362723802,0.4987628101871426,0.5037508165516283,0.5090125607997853,0.5145151338784122,0.5202232840606548,0.5261000441098016,0.5321073929732744,0.5382069269046561,0.5443605097673454,0.5505308661848374,0.5566820745610177,0.5627799111554501,0.5687919945602216,0.5746876884619079,0.5804377502627857,0.5860137771427303,0.5913876020307183,0.5965308930427609,0.601415221379894,0.6060127115981204,0.6102971403505861,0.6142451808018542,0.6178374936064243,0.6210594823473976,0.6239016605985055,0.6263596670445549,0.6284340090322592,0.6301296257246349,0.6314553530981366,0.6324233547045235,0.6330485615820978],[0.47508180342528245,0.4736053197432969,0.4723288075873404,0.47127402672167606,0.47046243282506717,0.46991484451940246,0.46965108365109626,0.4696895952148479,0.4700470551703453,0.47073797619436614,0.47177432299839805,0.4731651500788837,0.47491627550975507,0.4770300045127087,0.47950491596582767,0.48233572370693767,0.485513222487816,0.4890243258333167,0.4928521999963716,0.49697649483828144,0.5013736689560123,0.5060174028326585,0.5108790902385063,0.5159283945007007,0.5211338524349887,0.5264635044557844,0.5318855243652789,0.537368816296639,0.5428835391043152,0.5484015103326837,0.5538964336586435,0.5593438878870792,0.5647210181086164,0.5700058933346575,0.5751765631786707,0.5802099845964677,0.5850811756986894,0.5897630368298821,0.5942270648318941,0.5984447613514285,0.6023892696181004,0.6060368263172786,0.6093678152519733,0.612367378780895,0.6150256362406937,0.6173375957074377,0.6193028512240013,0.6209251476605695,0.6222118786307667,0.6231735646714728],[0.4777660323062721,0.47630597671194175,0.47502903145633174,0.4739547753355637,0.4731024271339937,0.4724905441588467,0.4721366997413343,0.4720571458463178,0.47226646850308174,0.47277724525200865,0.47359971508522425,0.474741472326343,0.47620719643366666,0.47799842972858697,0.4801134144839654,0.48254699963415515,0.48529062561273795,0.4883323935524979,0.49165722239183884,0.495247094432827,0.499081386686741,0.5031372819862916,0.5073902503450588,0.5118145873389587,0.5163839922321374,0.5210721639661549,0.5258533877302692,0.5307030783848052,0.5355982393347407,0.5405177865389844,0.5454426775911824,0.5503557765868925,0.5552413806777894,0.5600843445570817,0.5648687929815865,0.5695765679809802,0.5741858607087863,0.5786707332456502,0.5830019565131981,0.5871488310880969,0.5910812544653358,0.5947714995433355,0.598195503137405,0.601333659676645,0.6041711929166699,0.6066981998223575,0.6089094587518916,0.6108040822555865,0.6123850791796511,0.6136588745997119],[0.48038091381878223,0.4789332263780982,0.4776521931906344,0.47655535566715934,0.47565985485954415,0.4749821601820379,0.474537782064397,0.4743409743870231,0.47440443387096287,0.4747390048199077,0.47535339864614506,0.47625393836386093,0.4774443386130115,0.4789255317121653,0.48069554968062594,0.4827494711004814,0.48507944012289966,0.48767476290435763,0.4905220843526758,0.49360564534112117,0.496907617571999,0.5004085100706825,0.504087637855064,0.5079236395879426,0.5118950268604399,0.5159807430037067,0.5201607037839665,0.5244162857969035,0.5287307206690526,0.5330893442079109,0.537479639505192,0.5418910021555954,0.5463141457278433,0.5507400616431364,0.5551584698108678,0.5595558202325611,0.5639133129774868,0.5682060242661666,0.5724039562378608,0.5764743955916868,0.5803844085471918,0.5841028699867079,0.587601910791485,0.590857837514126,0.5938516186212219,0.5965690346381785,0.5990005813152669,0.601141202380393,0.6029899142585742,0.6045493709778043],[0.48292497246454014,0.4814863462260051,0.4801984312637533,0.47907687769437696,0.4781369089184212,0.47739307907323575,0.4768590187114959,0.4765471742362451,0.47646854773480773,0.4766324448626191,0.4770462392588621,0.4777151625529398,0.4786421292734474,0.47982760584170037,0.48126953228042335,0.4829633042781771,0.48490182182867103,0.4870756088385524,0.48947300590880044,0.4920804359868257,0.49488273979280295,0.4978635748551568,0.5010058686243068,0.5042923124085342,0.5077058786889442,0.5112303395856789,0.5148507587083349,0.5185539221714811,0.5223286670565925,0.5261660569702662,0.5300593445819539,0.5340036502385701,0.5379952742827596,0.5420305495950062,0.5461041354500484,0.5502066943772217,0.55432225686524,0.5584267978171829,0.5624896308951484,0.5664764073312101,0.5703519403433288,0.5740823744491854,0.5776367251091197,0.5809878867930549,0.5841132106923481,0.5869947460984908,0.5896192292120612,0.5919778913102536,0.5940661456963694,0.5958832005430642],[0.48539773556220245,0.4839656078827686,0.48266885489512423,0.4815213820370722,0.48053665411256374,0.4797274799290765,0.47910578885369,0.47868240448441124,0.4784668215645321,0.4784669930955919,0.4786891352666771,0.4791375582522122,0.47981453107975436,0.48072018858650883,0.48185248793492874,0.4832072212276687,0.4847780894506728,0.48655684129501686,0.48853347838633027,0.49069652610899855,0.49303336656559615,0.4955306272574067,0.49817461578117395,0.5009517871534037,0.5038492262106455,0.5068551227833799,0.5099592118808992,0.513153144835796,0.5164307501405536,0.5197881345048551,0.5232235654652226,0.5267370667468587,0.5303296466336965,0.5340020680212663,0.5377530568624757,0.541576835527286,0.5454599894533436,0.5493793615291802,0.5533039204315784,0.5571983116940745,0.5610258160734541,0.5647505754041668,0.5683391939602754,0.5717618203813175,0.5749928072692286,0.5780110366269974,0.5807999893880285,0.5833476265943871,0.5856461387652282,0.5876916092062281],[0.48779956573648775,0.48637209334909753,0.4850653438205342,0.48389162327584556,0.4828627942245818,0.4819900857773326,0.4812838989374963,0.4807536118242036,0.48040739045947695,0.48025201142784646,0.48029270323811546,0.4805330135331154,0.48097470935721076,0.4816177174631776,0.48246011109120696,0.4834981487665453,0.48472636943381964,0.4861377466804616,0.48772390290892387,0.4894753821069456,0.49138197733898104,0.4934331062281076,0.49561822448551507,0.4979272639220623,0.5003510772711441,0.5028818674763414,0.5055135737559955,0.5082421806586868,0.5110659093944381,0.5139852429211539,0.5170027275782871,0.520122484526506,0.5233493539465566,0.5266875839659411,0.5301389647003961,0.5337002956636229,0.5373601239265625,0.5410963853172174,0.5448784330766216,0.5486707117051304,0.5524357443622318,0.5561364024411333,0.5597375668569159,0.563207281841573,0.566517493343772,0.5696444551493701,0.5725688764083344,0.5752758744603835,0.5777547869636277,0.5799988877142285],[0.4901315025569368,0.4887075231100134,0.48739036297735916,0.4861908715206467,0.4851194609907013,0.4841859406852258,0.4833993488593217,0.4827677869039611,0.48229826095241346,0.4819965366203467,0.48186701298826,0.48191262215201547,0.4821347606589378,0.4825332588791335,0.48310639380896375,0.48385094994838984,0.48476233172780464,0.4858347294805804,0.487061339165578,0.4884346339387152,0.4899466832475388,0.49158951235984133,0.49335549210513274,0.4952377450590513,0.49723055037395614,0.4993297248821468,0.501532952895004,0.5038400312198031,0.5062529892567986,0.5087760365844126,0.5114152821797673,0.5141781603756076,0.5170724888871764,0.5201050739625532,0.5232797682925034,0.5265948958449883,0.5300402216161195,0.5335951358495441,0.5372302186217252,0.5409105374650188,0.5445986258590718,0.548256799987841,0.551848883410174,0.5553414337451065,0.5587045591032602,0.5619124033239951,0.5649433700462815,0.5677801465051513,0.5704095788966189,0.5728224424343444],[0.4923951156096389,0.4909740983520734,0.489646794236743,0.4884227342298663,0.4873110267858136,0.4863202142948486,0.48545812953345147,0.48473175629555715,0.48414709891378394,0.4837090658149278,0.4834213725562853,0.4832864699223818,0.4833055025913096,0.4834783035766925,0.48380342909155294,0.4842782376464386,0.484899016074481,0.4856611537628845,0.48655936465796795,0.4875879545913818,0.48874112913595613,0.49001333451961215,0.49139962107319407,0.49289601522011506,0.4944998820792949,0.4962102562879509,0.4980281135951385,0.49995655007330675,0.5020008293985115,0.504168251540533,0.506467788410961,0.5089094236961348,0.5115031258537215,0.5142573776316127,0.5171771950872397,0.5202616593263716,0.523501399611922,0.5268773339523446,0.5303617879372019,0.5339211649602782,0.5375187339516888,0.5411169466554837,0.5446792156558146,0.5481712116761783,0.5515617570392753,0.5548233891122393,0.5579326602141355,0.5608702322213542,0.5636208158215794,0.5661729963835251],[0.4945923706382478,0.49317435881258553,0.4918377865607172,0.4905909994741048,0.489441941996034,0.4883980345097853,0.4874660522968381,0.4866520102130046,0.4859610573625836,0.4853973863905692,0.48496416222916006,0.48466347519535435,0.48449632321219416,0.4844626275906127,0.4845612862398025,0.4847902673538521,0.48514674553687265,0.4856272809670503,0.4862280405510834,0.4869450580720257,0.4877745280691954,0.4887131255853021,0.48975834094280535,0.490908815329894,0.49216465914108803,0.49352773068001876,0.4950018479458155,0.4965929007561025,0.49830882440485846,0.5001593894812174,0.5021557556405503,0.5043097308084762,0.5066326739646403,0.5091339872650307,0.511819187582382,0.5146876992375111,0.5177308675687073,0.5209310808812778,0.524262588802394,0.5276935910668511,0.5311886848906382,0.5347110796714287,0.5382243839108563,0.5416939553617631,0.5450878640456124,0.5483775304472345,0.5515380996228847,0.554548606110534,0.5573919775079418,0.5600549174525002],[0.4967255098085732,0.49531105716031226,0.4939666252927634,0.4926995011257824,0.49151659729667635,0.49042434825256387,0.4894286097379446,0.488534565203212,0.48774664300607035,0.48706844853554854,0.48650271552977636,0.48605128085664584,0.48571508685449366,0.48549421496466005,0.4853879538077959,0.48539490404367097,0.4855131212940747,0.4857402970869142,0.4860739761826003,0.48651180675630445,0.48705181771291467,0.487692714882275,0.48843418495222485,0.48927719271311837,0.4902242534750402,0.4912796583463836,0.49244962541246873,0.4937423447432506,0.4951678796892273,0.4967378813830913,0.49846506849827865,0.5003624220195791,0.5024420498640235,0.5047137005115403,0.5071829743663259,0.5098494357868383,0.51270506532072,0.5157336321959857,0.518911313788222,0.5222083275254888,0.525591002576714,0.5290238047859811,0.5324710686116803,0.5358983641752377,0.5392735110141595,0.5425672812450115,0.5457538428270329,0.548810992399642,0.551720222498725,0.554466662162924],[0.4987969466364728,0.4973870502577362,0.4960366207065025,0.49475200583726886,0.4935392103992381,0.4924038095195819,0.4913508668006211,0.4903848602436896,0.48950961948353633,0.4887282780030976,0.48804324407507943,0.487456194119663,0.48696809195365803,0.486579237013449,0.4862893440427163,0.4860976559278712,0.48600309032361577,0.4860044194224438,0.4861004806699887,0.4862904143962421,0.4865739222020338,0.48695153748933834,0.4874248967296399,0.4879969969032282,0.488672420996097,0.4894575095073436,0.4903604516319496,0.4913912652510819,0.49256163035585226,0.4938845366650775,0.49537370432337213,0.4970427395909864,0.4989040013896052,0.5009671907971949,0.503237750819691,0.5057152877248937,0.508392361880117,0.5112540283749643,0.5142783201318346,0.5174375355863725,0.5206999646749896,0.5240316834654722,0.5273981765007748,0.53076567810238,0.534102209011549,0.5373783275916245,0.5405676323221776,0.5436470570028239,0.5465969988293063,0.5494013157027922],[0.5008091756728861,0.4994052071828505,0.4980510154392259,0.49675212114633743,0.4955137362800349,0.49434069338006503,0.4932373804008053,0.4922076840299795,0.4912549445901694,0.49038192576104783,0.48959080238007374,0.4888831694740206,0.48826007542222755,0.4877220817346191,0.4872693513247089,0.48690176635253446,0.4866190756881267,0.48642107078739466,0.48630778726297297,0.48627972765684674,0.48633809886236723,0.48648505528382824,0.486723936147373,0.4870594823794261,0.4874980151556651,0.48804755463489047,0.4887178536330372,0.48952031729368983,0.4904677766454867,0.49157408223835297,0.4928534856133229,0.4943197844845717,0.495985227783291,0.4978592170347451,0.49994690764319594,0.5022479015907192,0.5047552953156934,0.5074553366998,0.5103278109136434,0.5133470693222237,0.5164834606766487,0.5197048917957703,0.5229783075890663,0.5262709697589498,0.5295514862584557,0.5327905890873952,0.5359616817535566,0.539041187815543,0.5420087344429867,0.5448472035833798],[0.5027646966622232,0.5013683334925708,0.500012910023744,0.4987032236173929,0.49744379945535877,0.4962388340989361,0.49509214530592405,0.49400713072245706,0.4929867382135705,0.49203345066458337,0.4911492880553434,0.49033582946175447,0.48959425735456485,0.48892542612563855,0.4883299561593055,0.4878083539639495,0.48736115787114076,0.48698910758098396,0.48669333436830275,0.4864755670509279,0.4863383468460861,0.48628524199450385,0.4863210505125379,0.4864519766529682,0.48668576365602406,0.4870317622461767,0.4875009112634046,0.4881056041624704,0.4888594135133092,0.4897766462239833,0.4908717068999298,0.49215825855391554,0.493648192889564,0.495350460615141,0.4972698658037126,0.49940598630478283,0.5017524171621912,0.5042965104690361,0.5070196893843657,0.5098982803997504,0.5129047010269846,0.5160088028961106,0.5191791970373594,0.5223844447568917,0.525594053631575,0.5287792598583845,0.5319136040909769,0.534973321638855,0.537937573727451,0.5407885476706531],[0.5046659525794452,0.5032791108884459,0.5019252054012661,0.5006084055877507,0.49933264652099346,0.49810158520861453,0.49691856366346454,0.49578658104898765,0.4947082773302652,0.4936859308816377,0.49272147242828634,0.4918165175147639,0.49097241938082364,0.49019034366680947,0.4894713657512163,0.48881659072611944,0.4882272950273947,0.487705087542451,0.48725208660633984,0.48687110765766,0.4865658544527648,0.48634110463151575,0.4862028781047774,0.48615857423032904,0.4862170611376539,0.4863886979987455,0.48668526878116375,0.48711980450543324,0.4877062709970107,0.48845910173859275,0.4893925624210636,0.4905199474525741,0.4918526314157316,0.49339903133856555,0.495163575593546,0.4971458116802906,0.499339799696743,0.5017339126423345,0.5043110958417751,0.5070495476394419,0.509923708311924,0.5129054099886052,0.5159650487264176,0.5190726740624623,0.5221989320455837,0.5253158326647026,0.528397337458385,0.5314197784397194,0.5343621276019903,0.5372061395649118],[0.5065152807044504,0.5051400511951498,0.5037905610461665,0.5024704388365567,0.5011831169238923,0.4999317991079031,0.49871943532279767,0.4975487054233071,0.49642201418044657,0.49534149958059226,0.4943090564105542,0.49332637689552516,0.49239500982086726,0.4915164390966821,0.49069218210172527,0.48992390735614527,0.489213570108218,0.4885635632678097,0.4879768797699488,0.4874572809016965,0.4870094633764838,0.48663921600627635,0.4863535547353724,0.486160822623484,0.4860707392122099,0.48609438176791725,0.48624407947595716,0.48653320125376653,0.4869758191915052,0.48758623376792226,0.48837835528630963,0.48936494990807405,0.4905567792322169,0.49196168891706343,0.4935837303706565,0.49542242155461924,0.49747225682413126,0.49972255220081685,0.5021576623108824,0.5047575425472056,0.5074985760990062,0.5103545565863138,0.5132977164245837,0.5162997107781896,0.519332495284934,0.5223690633117486,0.5253840305107628,0.5283540697135984,0.5312582085275546,0.5340780068361934]],"zauto":true,"type":"contour"},{"autocolorscale":false,"autocontour":true,"colorbar":{"len":0.875,"tickfont":{"size":8},"ticksuffix":"","x":1,"y":0.5},"colorscale":[[0.0,"rgb(255,247,251)"],[0.14285714285714285,"rgb(236,231,242)"],[0.2857142857142857,"rgb(208,209,230)"],[0.42857142857142855,"rgb(166,189,219)"],[0.5714285714285714,"rgb(116,169,207)"],[0.7142857142857143,"rgb(54,144,192)"],[0.8571428571428571,"rgb(5,112,176)"],[1.0,"rgb(3,78,123)"]],"contours":{"coloring":"heatmap"},"hoverinfo":"x+y+z","ncontours":25,"visible":true,"x":[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],"xaxis":"x2","y":[1e-06,1.757510624854793e-06,3.0888435964774785e-06,5.428675439323859e-06,9.540954763499944e-06,1.67683293681101e-05,2.94705170255181e-05,5.1794746792312125e-05,9.102981779915228e-05,0.00015998587196060574,0.0002811768697974231,0.0004941713361323833,0.000868511373751352,0.0015264179671752333,0.0026826957952797246,0.004714866363457394,0.008286427728546842,0.014563484775012445,0.025595479226995333,0.04498432668969444,0.07906043210907701,0.1389495494373136,0.244205309454865,0.42919342601287785,0.7543120063354607,1.325711365590108,2.329951810515372,4.094915062380427,7.196856730011514,12.648552168552959,22.229964825261955,39.06939937054613,68.66488450042998,120.67926406393264,212.09508879201925,372.7593720314938,655.1285568595496,1151.3953993264481,2023.5896477251556,3556.4803062231213,6250.551925273976,10985.411419875572,19306.977288832455,33932.217718953296,59636.23316594637,104811.3134154683,184206.99693267164,323745.754281764,568986.6029018281,1000000.0],"yaxis":"y2","z":[[0.1421214828079791,0.1385712299070121,0.13491828039321857,0.1311949068870602,0.12744083538353906,0.12370356679782728,0.12003827802866289,0.11650708980441951,0.1131774588437035,0.11011946523552449,0.10740185916685621,0.10508693755953825,0.10322464325839834,0.10184665423993035,0.10096151643121631,0.10055189601284834,0.1005746835504139,0.10096404590032303,0.10163683580317577,0.10249931001113781,0.1034540186671912,0.1044059624429833,0.10526750065798943,0.10596186415348087,0.10642538571663035,0.10660869152961319,0.10647712842436054,0.10601067432701551,0.10520352620870091,0.10406350103373477,0.10261132933089805,0.10087986978312175,0.09891322528026629,0.09676569525395057,0.09450045838978,0.09218785294829586,0.08990312580401266,0.08772357840214852,0.08572516638718794,0.08397880487907634,0.08254684402182352,0.08148031091220793,0.08081745175594146,0.08058380262291713,0.08079355366569468,0.08145156037372821,0.08255521422399902,0.08409559094770777,0.0860577276387863,0.08842030716077375],[0.13953996802909555,0.13569042112148264,0.13171278558755334,0.12763995764332103,0.12351344903951106,0.11938410212394197,0.11531242771167467,0.11136829774990038,0.10762964671366466,0.10417979277865178,0.10110304219248877,0.09847846461563312,0.09637217629020355,0.09482909494052144,0.09386572091324968,0.09346570661716574,0.09357952591262525,0.09412850719775145,0.09501230080581438,0.09611807424363192,0.09732964874805984,0.09853527389641897,0.09963342526043127,0.10053659282933804,0.10117337276970441,0.10148929898759068,0.10144683353186316,0.10102485350004373,0.10021787693625217,0.09903518467262876,0.09749992487557665,0.09564822880705623,0.09352831336531545,0.09119949249606468,0.08873096421265322,0.08620019020472966,0.08369066160614047,0.08128888265400462,0.07908054427397442,0.07714612086190355,0.07555645967335478,0.07436920130450785,0.07362686793257016,0.07335704859766687,0.07357439277001841,0.07428344538424707,0.07548111932762551,0.07715795548092653,0.07929804367247033,0.08187814647145003],[0.13701611080687426,0.1328618966310257,0.1285506416732265,0.1241149538436767,0.11959714817410665,0.11505044477917079,0.11053990121496308,0.10614277364673623,0.10194785673821039,0.09805321036352785,0.09456162303991145,0.09157332928052336,0.08917605556216843,0.08743346925171733,0.08637427996361029,0.08598493554853733,0.08620835777679683,0.0869493914376508,0.08808545334172024,0.08947947816782931,0.09099225440142515,0.09249226197426913,0.0938623715233857,0.0950036703339158,0.0958370961142561,0.09630361190345946,0.09636352788074325,0.09599540205341135,0.09519479751545963,0.09397305839901793,0.0923561857610559,0.09038383587255873,0.0881084125652501,0.08559417000643621,0.08291617482844689,0.0801588993096516,0.07741415110572641,0.07477803752115617,0.07234678595093591,0.0702115631141021,0.06845294042878708,0.06713615972190946,0.06630851147426012,0.0659996282227905,0.06622437622736248,0.0669868815920032,0.06828381038955168,0.0701056419770483,0.07243590696310233,0.07524941332213472],[0.13458823025374042,0.13012910257502497,0.12548070102288877,0.12067423179305996,0.11575150746222697,0.11076668632042899,0.10578794200278432,0.10089876438631414,0.09619837534132131,0.09180045824810361,0.08782912397268193,0.08441097650518213,0.08166266155953751,0.07967473138411363,0.07849489823083584,0.07811564426512818,0.07847094557655347,0.07944381650681046,0.08088211504426047,0.08261739286932274,0.08448186518667401,0.08632079272714446,0.08799987329785514,0.08940859332621018,0.09046087125922918,0.09109415387913233,0.09126778351089082,0.09096113859303016,0.0901718240528562,0.08891404683834817,0.08721723063804826,0.08512487581700161,0.08269363305268956,0.07999251257518179,0.07710207946962837,0.07411338170764474,0.07112623441220901,0.06824639415426452,0.0655812094403776,0.06323367301630332,0.06129550691823045,0.059840803848521425,0.05892226732874911,0.05857154415206336,0.05880339850201421,0.05962148613247039,0.06102272050579327,0.06299833071599573,0.06553185870395392,0.06859600108635508],[0.1322976646947466,0.1275396658938724,0.12255750691845978,0.11737974018403075,0.1120460883256162,0.10660971985568782,0.10113973386951122,0.09572363645350047,0.09046932603237386,0.08550566483191602,0.08098010198763547,0.07705122926375325,0.07387419358737955,0.07157857429520519,0.07024229005723326,0.06986984858179598,0.07038461212069375,0.07163951553713904,0.07344172868918471,0.07558123397869947,0.07785458186152582,0.08008013512592478,0.08210541380188173,0.08380896842664128,0.08509919411738268,0.08591179105506416,0.08620686322499255,0.08596614782519024,0.08519057816699095,0.0838982376843538,0.08212270101774798,0.07991173713585414,0.07732633937271557,0.07444002389083136,0.07133827779368122,0.06811791918930386,0.06488594723935719,0.061757250047008994,0.0588504343458947,0.056281293206276596,0.05415430633643161,0.052554029394937966,0.05153948588890077,0.05114432239671436,0.051382808789377246,0.052258220056228856,0.05376865748770784,0.055907400758610074,0.058658722861695455,0.061992692638937176],[0.13018770389309745,0.12514425364689064,0.1198401508587495,0.11430002453634037,0.10855976392328279,0.10266922894589714,0.09669549666624562,0.09072660250061486,0.08487549747354563,0.07928342511621544,0.07412095165339457,0.0695834190333545,0.06587622573873456,0.06318607397502098,0.061640218731173375,0.06126680663807822,0.06197676718135213,0.06357940589547963,0.06582343349572324,0.06844243982610496,0.0711885143141902,0.07384986217163239,0.07625618503881854,0.07827724943875725,0.07981865506889532,0.08081701530518254,0.08123552047553698,0.08106019096512473,0.08029683357773332,0.07896861451642953,0.0771141516207234,0.07478605326572152,0.07204986259279546,0.06898338116378645,0.06567631847023131,0.06223010598756035,0.058757487915010814,0.055381150803445044,0.052230292491291824,0.04943399853685504,0.047111169355380164,0.04535890892269679,0.04424391844335873,0.043801934499354135,0.044046302092762155,0.04498031332988994,0.04660494695443274,0.04891749644132675,0.0519036408249175,0.0555294560385923],[0.12830213456322406,0.12299490330613831,0.1173904191795515,0.11150828278468859,0.10537888106829596,0.09904631850071192,0.09257218226448302,0.08604035040451331,0.0795629648521035,0.07328731679331638,0.06740233504199097,0.06214099683724939,0.05777095598734357,0.05456212766358386,0.05272483481819196,0.05233480486102391,0.05328922965382657,0.05532968016109595,0.05811635038745994,0.06130467054380798,0.06459239457748248,0.06773639598085235,0.07055173357779423,0.07290390358961825,0.07470005519155946,0.0758813491251418,0.07641691897410767,0.07629926451674149,0.07554075707956308,0.0741709626015876,0.0722345648119491,0.06978975586245366,0.06690704159486824,0.06366847344936079,0.06016734674625541,0.0565083493061023,0.052807929499140684,0.0491941969095271,0.045804981048241385,0.04278208098662197,0.04026016365146661,0.03835149344283578,0.03713256561897507,0.03664161234000041,0.03689070365144481,0.03788418936207836,0.03962885468643333,0.04212873613419416,0.045370954696042735,0.04931445668819678],[0.12668342116978512,0.12114281787431481,0.11527016438031774,0.10907931811633516,0.10259389698263424,0.09585012907223935,0.08890069981939358,0.0818200471785309,0.07471172503715326,0.06771853379766747,0.06103567759142723,0.05492501540341876,0.04972188295802731,0.045812670255047316,0.043551200906742776,0.04311410817451054,0.04438682802147631,0.046995611359145525,0.05045795875620846,0.05432010786444111,0.05821780931614976,0.061881267847872456,0.06511919277204992,0.06780063337654547,0.06984041284680145,0.07118866716731174,0.07182357970984617,0.07174632087537004,0.07097743342401497,0.06955414217160219,0.06752825253620613,0.06496444535172735,0.06193889601556849,0.05853825769751201,0.05485914539719403,0.05100829900089281,0.047103489388303776,0.04327479014976971,0.03966488319175183,0.03642568158272966,0.03370776022339258,0.03164146651933152,0.030316412603125807,0.029774516031140886,0.030026636495344643,0.031080546394440856,0.03295375311064473,0.03566024403885604,0.0391864738380648,0.04347783129066266],[0.12537060543657058,0.11963570574522413,0.11353795174112147,0.10708535653812988,0.1002942721550739,0.09319184782882735,0.08581943119336422,0.07823747159593111,0.07053288776136897,0.06283053109664681,0.055311307007736635,0.048239968460264654,0.04200161417552243,0.03712436644108946,0.03420908733218548,0.0336632976308146,0.03537782170327621,0.038755680741463704,0.043068157703508074,0.047714954837429074,0.05227523398625081,0.056470092241995166,0.06011790283003957,0.06310264474409372,0.06535412819235598,0.06683595744968779,0.06753809034741627,0.06747206250701686,0.06666774174347911,0.06517094220591566,0.06304149586051284,0.060351548270053595,0.05718397843233086,0.05363097833391327,0.049792986409399005,0.04577833521622683,0.04170405892008263,0.03769808494578358,0.033902096175575054,0.030472260580208632,0.027572213250073155,0.025352579213341792,0.02392106933018452,0.023326261927098454,0.0235791834498499,0.02469613812701187,0.026713182233101682,0.029656259139797383,0.03350359229556634,0.038175510756460265],[0.12439707833787383,0.11851485477378157,0.11224519945391152,0.10559094482183036,0.09856174511671505,0.09117594687234853,0.0834631399661671,0.07546784735076105,0.06725524582452794,0.058920734653376966,0.05060718694370652,0.0425380464189397,0.03508217395754538,0.02886745112377654,0.024872239464119525,0.024078407565282553,0.026473276670050328,0.03094200132399988,0.03631149971663712,0.0418249703838524,0.047050388204280674,0.05173838333585759,0.05574037980425857,0.058967845684190535,0.06137190183431553,0.06293261483474102,0.06365301580937614,0.06355550891813747,0.06267950532408946,0.06107965299510539,0.05882428735533614,0.0559938637972191,0.05267923294969569,0.04897973751496001,0.045001289894144335,0.040854862357065626,0.03665616001304274,0.032527465919292335,0.028602220508722104,0.02503080097293718,0.02198117288961761,0.019622678824207766,0.01808745533323573,0.017437492303276087,0.017689092493649364,0.018877931614742684,0.02106945533524311,0.024296513153816687,0.028510350327116556,0.03359006661196872],[0.12378844206758695,0.11781224026712163,0.11143222031122421,0.10464746817673048,0.09746265577331609,0.08988934517480093,0.08194763991230977,0.07366840292405007,0.06509650092828036,0.056296115287867085,0.047360688025031766,0.0384345291681957,0.029767624197223064,0.02187589627485627,0.01600996868302345,0.014583413590548724,0.018204450536628173,0.024232991510951037,0.03079241552080987,0.037126541740713025,0.04290693831762704,0.04796472931605872,0.05220381743180425,0.055569461502276575,0.05803522327789565,0.059596842798127846,0.06026904378966532,0.06008368340568184,0.059088524473910796,0.05734623849698704,0.0549333751461989,0.051939082003197745,0.048463385209805164,0.044614892818000934,0.040507914747283394,0.036259285140028595,0.031985706497844435,0.027803193677945395,0.023830783890754503,0.020199800057450142,0.017064978241772204,0.014602522365309316,0.012972892492942822,0.012265241710561755,0.012516631174350423,0.013804582266222627,0.016231735635632488,0.01981016066358342,0.024430830711141178,0.0299206085618848],[0.1235607158777237,0.11754804166029499,0.11112472392003747,0.10428812671438321,0.09704057438255685,0.08939034136537972,0.08135278129203811,0.07295163840140056,0.06422063362798817,0.055205546067759764,0.04596737986859203,0.036588426949125986,0.027187947837327506,0.01798072452860338,0.00963920566030469,0.006426758155933287,0.012330994676087049,0.019984455764195913,0.02739926905671322,0.03420269483090969,0.040243853046470275,0.04543595026618166,0.04972453821558648,0.05307802660646239,0.05548399504375266,0.05694747503479452,0.05749004853615575,0.0571493274439829,0.05597859546003344,0.0540464527529691,0.051436300976271145,0.048245472723281425,0.044583760405896275,0.04057105457463811,0.03633380601471165,0.032000181149699714,0.027694280687801002,0.023530908005395017,0.019614191346221735,0.016044922196738948,0.012939306198670751,0.010449534502918283,0.008752671480288974,0.00798754913215017,0.008255713669298594,0.00971753620525263,0.012484551068346051,0.016476641217994432,0.021500454569150854,0.027348668657855544],[0.12371912972361669,0.1177289448318862,0.1113313754834477,0.1045243362424015,0.09731083909806792,0.0897000403660915,0.08170846256963533,0.07336146450170829,0.06469511494713885,0.05575883354629352,0.04661974267726634,0.03737152118772198,0.02815757444895762,0.019252491231641085,0.011472251086322511,0.008291768635069892,0.01286464129548623,0.01990095341568842,0.02697997711064536,0.033541323671034955,0.039376163381217626,0.0443749696778533,0.04847256313348857,0.05163161293560228,0.05383642655408008,0.055090231193996725,0.05541388624743272,0.05484527380663312,0.05343902956745874,0.051266410680386475,0.04841512295758451,0.04498889906573886,0.04110654432705037,0.03690004699390838,0.032511190921017855,0.028085961520810995,0.023766095713968944,0.019677924021234278,0.0159211881870602,0.01256541419637013,0.00966542993182446,0.00730043244560374,0.005614550767972551,0.004815914539554229,0.005179789468549429,0.006975073843936454,0.01017543113259197,0.014554338150297354,0.019885904552963365,0.02597591124498027],[0.12425768520262245,0.1183475156560728,0.11204287971509996,0.10534434915028967,0.09825840709304755,0.09079886503962069,0.08298868293232856,0.07486244543132509,0.06647000644748806,0.05788240907076198,0.04920265308147538,0.04058776111315184,0.032299474821411746,0.024830255911109076,0.019187911206102526,0.017050536286444356,0.01917039646206636,0.023941090969241085,0.029596215648235148,0.035219815528268014,0.04038043262206671,0.04485534561725629,0.04851942114105375,0.05130129977746589,0.05316471063456828,0.0540998146334811,0.05411895132924053,0.0532545123663605,0.05155792753629052,0.049099253575943316,0.04596705669571619,0.04226834044329668,0.0381282446514109,0.03368913041675139,0.02910843212892137,0.024554222223554075,0.020196718895208687,0.016193171644562788,0.012664232286441675,0.009666886138718625,0.007186540408164897,0.00518114259541093,0.003685482533242016,0.002982008028832194,0.0036714438420325877,0.0059333551040336155,0.009484636383931325,0.014091442179497315,0.019573816567156635,0.02576778562055267],[0.12515955382090188,0.11938275798905355,0.11323277949469086,0.10671442633447115,0.099839625109155,0.09262932508068304,0.08511605499644986,0.07734753102757959,0.06939204949638324,0.061347054334105276,0.053353542560586276,0.04562124044182117,0.03847214242396135,0.03240488073102192,0.028130855160869984,0.026380781923095356,0.0273361734811207,0.03034304905395624,0.034432338386522696,0.038830808923029585,0.043041917438387214,0.04676292830908057,0.049808949788101894,0.05206777450132661,0.053475400673907596,0.05400285317892428,0.05364899670882685,0.05243660500644537,0.05041027647228923,0.047635441009077524,0.04419802297313201,0.0402044765913532,0.035781968509348776,0.03107847128365139,0.026262426715633395,0.021521313651445627,0.017057504010721505,0.013077075250770731,0.009760780531022327,0.007200435141758394,0.005317882231866684,0.0038884728899128414,0.0027848012001391942,0.0024445439031515913,0.0036909304748420657,0.006349175383018195,0.010109787203678633,0.014823903757560188,0.020356075029253837,0.026564533223594092],[0.12639825455682183,0.12080176260560195,0.1148598139024225,0.10858229260419965,0.10198743935076073,0.09510413964914677,0.08797497936727014,0.08066045289679756,0.07324493252691124,0.06584531470723119,0.0586235261727477,0.0518036628197428,0.045691208292593356,0.040679981368982855,0.0372072760167878,0.035606512006331206,0.03589985341873342,0.0377313037474373,0.040535926190721994,0.04375949721456414,0.04696483352707161,0.049840110533781914,0.05217294352553135,0.05382342085407314,0.05470441769347342,0.054768761899400005,0.05400123478660441,0.052413719840592315,0.05004236931669257,0.046946076246851494,0.043205803535519643,0.03892448122659551,0.03422728411627594,0.029262184600523766,0.024200783899857994,0.01923961175581511,0.014602312993946273,0.010542335870901958,0.00733558336063693,0.005197861851334458,0.004012621752664845,0.0032472321007965704,0.0026105797032625797,0.0027929078822890373,0.004570535537521317,0.007586184757180327,0.011565434211637911,0.016393770332422435,0.02196606168792906,0.028164017313235912],[0.12793943985043185,0.12256217498306099,0.11687138908325106,0.1108821172454635,0.10461870573054802,0.09811724139703377,0.09142867536756395,0.08462287352390616,0.07779385395392915,0.071066372907667,0.06460352777517761,0.05861354897684074,0.053350436569933185,0.04909715092060539,0.04611613124422841,0.04456466891663208,0.04441235642052682,0.045425663352772754,0.04723921313485544,0.04945817341001856,0.05173044384504637,0.05377471164442891,0.05538070422645894,0.05639901264865439,0.05672972683641169,0.0563131146277426,0.05512285446628841,0.05316144776711148,0.05045728748861105,0.047062933267795426,0.04305425531115968,0.03853020975249206,0.03361310168217325,0.02844931660674125,0.023210755069954868,0.018097851345958437,0.013346786900271957,0.009247362473123277,0.0061739933251369825,0.004499923834750694,0.003992329602776862,0.003772086783922501,0.0035786772843339983,0.004169509048708341,0.006210486897191059,0.00946483267086653,0.013642073418726863,0.018594580370522175,0.024216585514954196,0.03040341348591778],[0.12974304926074057,0.124615108811392,0.11920756969461764,0.11354005498556474,0.10764198472522182,0.10155487685389986,0.09533513022235605,0.08905732467279256,0.08281795099608091,0.07673917290188013,0.07097154671511793,0.0656933685591191,0.061102511675766476,0.05739532589777933,0.05472950362570697,0.05317746861820451,0.05269068774646229,0.05309800176300563,0.05414179295763794,0.055531330138985625,0.05698814488598391,0.05827217744835067,0.05919105407163993,0.05959953594473694,0.05939495438112108,0.05851190955862743,0.05691764574380676,0.05460852452986313,0.05160759237101323,0.047963099815530645,0.04374781849781245,0.03905905121826878,0.03401933448143066,0.02877804510116999,0.023514597642535728,0.01844500351151707,0.013835596734127237,0.010026743624448007,0.007424885956821857,0.006233309456586993,0.005964702284672229,0.005902077336291415,0.005965080409166866,0.006751173058561215,0.00881421499658867,0.012107256111198093,0.01636262012675239,0.021380445947353114,0.027024906340494752,0.033185181353786335],[0.13176557454433593,0.1269081250713614,0.12180501973540066,0.1164794801723689,0.11096449757551595,0.10530479625503697,0.09955901575071247,0.09380198735871366,0.08812680173201984,0.08264604103729799,0.07749103461942604,0.07280733687950622,0.06874414869758451,0.06543594473686043,0.06297728588199311,0.06139681865200913,0.06064084572553555,0.06057540498938097,0.06100717170541253,0.061714161980113695,0.062474776799653506,0.06308826251446222,0.06338562072792199,0.06323338559864639,0.06253330521907227,0.061220243949307016,0.05925969354802406,0.05664558951240708,0.05339872353778635,0.0495658466550662,0.045219493691771556,0.04045858638120894,0.035409985874421186,0.030231391608529588,0.025116316280738633,0.020301868993103146,0.01607685635596396,0.012769088324106755,0.01063873145083344,0.009629440340911682,0.009297276559017726,0.009225791161211576,0.009429655180675718,0.010333181647285698,0.012359009150655577,0.015568173389770507,0.019771835595962614,0.024758297590934675,0.03036261176536889,0.03645671939887158],[0.13396221230977778,0.1293879656833301,0.12460046392779323,0.11962533520622676,0.11449749963594817,0.10926268303164913,0.10397890888682354,0.09871775718278213,0.09356501426590538,0.08862010307187491,0.08399340529491056,0.07980038605887897,0.07615157797970819,0.07313836935459274,0.07081639918347572,0.06919067216823968,0.06820769970045903,0.06775839206551623,0.06769130437390952,0.06783180021956954,0.06800139508123008,0.06803316321338419,0.06778178514523144,0.06712883604978813,0.06598475047057685,0.0642888879472954,0.062008766746248216,0.05913914849563834,0.05570136958695171,0.051743142526067966,0.047338971446355356,0.04259131415808001,0.03763264142500889,0.03262848428069606,0.027781021512747976,0.02333040141556088,0.019543442249844677,0.01666414122622149,0.0148013494691873,0.013819038315119107,0.013406339069250735,0.013334026220685984,0.013651899598114772,0.014658300893600453,0.016662096434588883,0.019758125437920267,0.02383430927945429,0.02870603581155664,0.034200895407409296,0.04017739530480147],[0.1362887423957004,0.13200283930071402,0.12753343015403987,0.12290734213382377,0.1181598863216891,0.11333589949178285,0.10849058679683163,0.10368993212518111,0.09901032570770821,0.09453692802668989,0.09036019409717508,0.08657002389392163,0.08324733218262295,0.08045356935041757,0.07821980730334833,0.07653799734401501,0.07535718542448196,0.07458633602585249,0.0741033143968915,0.07376764523750681,0.07343394372248635,0.07296353082341481,0.0722330203097678,0.07113982401519044,0.069605189382659,0.06757558259728813,0.06502315273541502,0.06194583447558854,0.05836747192164077,0.054338212295947645,0.04993532338233613,0.04526449865949653,0.040461539801788834,0.035693819492917875,0.031159586229600855,0.02708000356136258,0.023673541439970143,0.021101114141403123,0.01939314600242209,0.018421582600515102,0.017983090608514763,0.017953257242586992,0.018389397415526868,0.01950204615636442,0.02151234034386935,0.024511880335394327,0.028439353824462832,0.033149702419034345,0.038482920860113214,0.044295361024369304],[0.13870304081277934,0.13470416805268237,0.13054820594331762,0.12626208660574567,0.12188021988812346,0.11744510456309322,0.11300763443854436,0.10862688694681569,0.10436911465637709,0.10030561071902147,0.0965091297072303,0.09304867764760683,0.08998280084133406,0.08735201124287321,0.08517157197492704,0.0834262633346323,0.08206864146990354,0.08102155881565082,0.08018458099245304,0.07944293317495293,0.07867718890155338,0.07777215401401699,0.07662402939312175,0.07514559974490106,0.07326966343679842,0.0709511405548495,0.06816833261457411,0.06492374310961326,0.06124476736828232,0.0571844525650102,0.0528224090179523,0.04826577597577283,0.04364979692096622,0.039136820290467535,0.03491109353961089,0.031164542701859435,0.02806764964598688,0.025725602582076318,0.024139354320595875,0.023210290752507436,0.022808186115922616,0.02286611404984668,0.02343624859370643,0.0246664643041391,0.026712150441571957,0.0296476450369646,0.033438965965712886,0.03797640870679221,0.04312180096546872,0.04873960640017028],[0.14116619919525894,0.1374477935249861,0.13359506389476658,0.12963413754464476,0.12559753190554124,0.12152441024849375,0.11746048738955596,0.11345741374922716,0.10957143821606175,0.10586115090642742,0.10238416403288783,0.09919273307787392,0.09632856663629186,0.09381739429702717,0.09166416486511389,0.08984988497234118,0.08833094752529265,0.08704132217694953,0.08589733634190543,0.08480422072299099,0.08366333794126694,0.0823791032980653,0.08086493031548496,0.07904791790839844,0.07687230822544837,0.07430193076307481,0.07132191813019852,0.06793996700373862,0.06418735699944034,0.06011984484265594,0.05581840926043593,0.05138958593693082,0.04696470926947292,0.042696647519761884,0.03875157305775434,0.035292537158777046,0.032453144921739896,0.030306623719072223,0.02884723225687946,0.028004946104173763,0.027696247627498612,0.027884222909425018,0.028609992168202678,0.029974900317636843,0.03208475512151094,0.03499309742031379,0.03867792877350606,0.04305572241174541,0.04801127454099436,0.05342301618939009],[0.1436432695059032,0.14019469862100106,0.13663087686735903,0.13297642551283403,0.1292612758262862,0.1255206543193851,0.12179471719312034,0.11812770714031506,0.1145665034088118,0.11115846178089576,0.1079485103428945,0.10497559072066429,0.10226870871088604,0.09984305161327861,0.09769677979491397,0.09580912986131417,0.09414032220918449,0.09263345799786807,0.09121820926434454,0.08981578207049282,0.08834447120704539,0.08672515421210684,0.08488624285872677,0.08276783558003756,0.08032501810874092,0.07753039997267289,0.07437604291383237,0.0708749438943937,0.06706219259695154,0.0629958339134815,0.058757314590465064,0.054451142365750466,0.05020298365614475,0.04615485872155808,0.042455554091696115,0.03924458785233186,0.03663047145884952,0.034669611987557795,0.033358217575080444,0.032648106675852745,0.032483765641296326,0.0328416594745287,0.03374893222857141,0.03527075556792171,0.03747470571243787,0.04039408518732528,0.04401002857786532,0.04825655815940238,0.053038525820490644,0.058250155770152724],[0.14610368136964477,0.14291133098608552,0.13961926507618055,0.13625009990708184,0.13283074794020672,0.12939221297135242,0.1259690608516134,0.12259847930189484,0.11931885220797693,0.11616780851413162,0.11317977041236564,0.11038312129861198,0.10779723095314318,0.10542968824779386,0.10327416191568801,0.10130929810120246,0.09949894905838648,0.09779382631069371,0.09613443711022963,0.09445496540393543,0.0926876531412997,0.09076724184938215,0.0886351254743623,0.08624299889609205,0.08355591782283553,0.08055478515066347,0.07723833367558704,0.07362468397944995,0.06975252071202977,0.06568184640631605,0.06149412496207734,0.0572913932230371,0.053193584243326535,0.04933292726282712,0.04584413265298902,0.042849768062234034,0.04044262387379789,0.038670877903417715,0.03753474831039717,0.037000372599980694,0.03702695180850202,0.03759367454888225,0.03871202169181385,0.040417628817784705,0.042747665016364296,0.045717049615624415,0.04930530513564886,0.053457456533399485,0.05809435449216565,0.06312536619002396],[0.14852139240453055,0.14556962075275476,0.14253041023287139,0.13942405097245816,0.1362742154266983,0.13310763141274876,0.12995347103104823,0.12684240146348547,0.12380526166474076,0.12087136379240222,0.1180664719455408,0.11541058067637044,0.11291569173710082,0.1105838515719518,0.1084057413712625,0.10636008636097721,0.1044140648580624,0.10252476405691018,0.1006415805738898,0.09870933863031378,0.09667182798491475,0.09447545799908205,0.09207277299385132,0.08942565342130249,0.08650811104039992,0.08330865377133632,0.07983223514579585,0.07610180850955647,0.07215947333115573,0.06806712315179793,0.06390636965365351,0.05977731231317482,0.05579545750254577,0.05208585405243457,0.048773571194802474,0.045970497337886454,0.043760542368373054,0.04218820901947579,0.041256866621107,0.04094002087739659,0.041201777275424296,0.04201667398443358,0.0433792328396244,0.045299738396847714,0.04779030146150625,0.05084949976738189,0.05445288134772296,0.05855197244115851,0.0630798224141953,0.06795918222641088],[0.15087483362940426,0.1481467788308776,0.1453406508850675,0.14247423904245252,0.13956791527799775,0.13664423856294378,0.13372732005372323,0.1308419194129943,0.12801226182413916,0.12526059609293888,0.12260555618523136,0.12006043776435325,0.11763154952405287,0.1153168342945502,0.11310496385856525,0.11097508455171104,0.10889732702200677,0.10683410321583518,0.10474211633492436,0.1025749277577297,0.1002858762630823,0.09783113601774447,0.09517272560947611,0.09228132767362208,0.08913883149308126,0.08574055539171188,0.08209713168036968,0.07823603733256981,0.07420272207133648,0.07006121369090523,0.0658939571194405,0.061800461524746275,0.05789410775975739,0.05429630403626044,0.05112732057750855,0.04849399313490134,0.04647634248383071,0.04511744233207913,0.044421651030486446,0.04436356095612269,0.044904425602645334,0.04600847274721399,0.0476519453229395,0.0498223110589934,0.052510273724157966,0.055699931144303376,0.05936184825085633,0.06345115708803112,0.06791006003053505,0.07267268427938854],[0.1531467068437756,0.1506249487531915,0.148031947986358,0.1453829323703009,0.14269502834979267,0.13998683581004462,0.13727780788373536,0.1345874229786201,0.13193415436257988,0.12933426813844168,0.12680051195735392,0.12434079065836229,0.12195695503527576,0.11964384833656477,0.11738875441821159,0.11517136721229085,0.11296435432113365,0.11073452543739265,0.10844455112555543,0.10605512271194495,0.10352740998603353,0.10082566435572188,0.097919828504245,0.09478804188259626,0.09141896471622606,0.08781387204630102,0.0839884855440558,0.07997450736198151,0.07582078949734562,0.07159400398937127,0.06737856115967507,0.06327534638267575,0.05939862855832187,0.05587033132929362,0.05281099590395735,0.05032759705453777,0.048500159496021315,0.04737129129552225,0.046943479111708084,0.047186445854233164,0.0480518324687419,0.04948864797864672,0.05145331334663317,0.053911903011249276,0.05683624591261601,0.060197598286520396,0.06396133273755479,0.06808447254876622,0.07251616157375428,0.07720009118411017],[0.15532368231707103,0.15299076993090824,0.15059128600712252,0.1481379213455523,0.14564468997429286,0.14312650182627606,0.14059858041736567,0.1380757240797897,0.13557142503673436,0.13309688082162896,0.13065995562656735,0.12826417203430804,0.1259078318895359,0.12358337388771559,0.12127707062489991,0.11896914743565548,0.11663437086544212,0.11424311125077528,0.11176283936845634,0.10915997968509616,0.10640201871375171,0.10345975910732216,0.10030961712915115,0.09693587858443783,0.09333284996559034,0.0895068608185555,0.08547808365589689,0.08128213221911965,0.07697136867613308,0.07261578254412032,0.06830318101946407,0.06413823504726304,0.06023966562510678,0.05673462228195438,0.05374936894523156,0.05139622410792774,0.049758670234991795,0.04887908707052015,0.04875459751010185,0.04934388144440267,0.05058235941409178,0.052399038856986,0.054728684164358665,0.057516700361736,0.06071791240913551,0.06429225005217874,0.0682002180847656,0.07239988800435891,0.07684589377070596,0.08149005968402591],[0.15739603560905235,0.15523489582018576,0.1530100550186052,0.1507317516757307,0.14841106980390348,0.14605952722342233,0.14368854344593718,0.14130879280659833,0.13892946154697206,0.13655744314944945,0.1341965228346077,0.13184661737777997,0.12950314728504556,0.12715662184411952,0.12479251134830392,0.12239146421204702,0.11992990125694206,0.11738098878574563,0.11471596121739273,0.11190573821305448,0.10892276437304182,0.10574299357047164,0.1023479442319104,0.09872676375695803,0.09487825584630814,0.0908128391291783,0.08655441383091307,0.08214210842233692,0.07763184967322732,0.0730976297193012,0.06863220504534917,0.0643467202961278,0.06036838932690008,0.05683496993007875,0.05388466716154744,0.05164097121533944,0.05019444092697431,0.04958699377537963,0.049805966943432395,0.05079188911306867,0.05245675680956014,0.054704502136921386,0.05744615532447203,0.06060685283049525,0.06412602687953861,0.0679538416094212,0.07204669391977678,0.07636353330090391,0.08086368141935434,0.08550609129644901],[0.1593572533081034,0.15735149823390893,0.1552834437289222,0.15316100128168386,0.1509925352743487,0.1487864773589673,0.14655084937224064,0.1442927044928873,0.1420175068854585,0.1397284818861068,0.1374259805902804,0.13510691273655745,0.13276430802876274,0.13038706663543226,0.12795995334710722,0.1254638766836526,0.12287647543368815,0.12017301325810002,0.11732756046125725,0.11431442421462877,0.11110977704572045,0.10769342962089754,0.10405069762415656,0.10017432244578017,0.09606641907719314,0.09174043893582683,0.08722314606997875,0.08255660550859076,0.07780015982371247,0.07303230014103708,0.06835217752325728,0.06388018406894488,0.05975649720946373,0.05613577640287703,0.053175756499278845,0.051018388042903866,0.04976575417792483,0.0494586383706458,0.05006855902202892,0.051508872026158496,0.05365961402629083,0.056394042460093004,0.059597337794869504,0.06317486724131831,0.06705241650404639,0.07117219485665387,0.0754876782994042,0.07995907473067294,0.0845501308730443,0.08922632735018529],[0.1612036296310856,0.1593377792291033,0.15740986206797397,0.15542561364593527,0.15339090208321035,0.15131137393145708,0.1491920320533066,0.14703675729666005,0.14484779401532952,0.14262522831359845,0.14036649619915403,0.13806596534491117,0.13571463754946486,0.13330001812666664,0.13080619275326177,0.12821414195174188,0.12550230946727733,0.12264742517627121,0.11962556815722589,0.11641344347743485,0.11298983896450124,0.10933722684299291,0.10544347987810952,0.10130368209369217,0.09692202916663406,0.09231383160702977,0.08750765197343333,0.08254761963209852,0.07749595909990285,0.07243570962320588,0.06747343943722477,0.06274135048065968,0.0583973679127847,0.05462055581958153,0.05159801634050903,0.04950017009332563,0.048446821823447575,0.048476316405158766,0.04953544209902052,0.051498025289835186,0.05420152371369852,0.05748241964011213,0.06119834577992348,0.06523603574173173,0.06950992538312219,0.07395654321814649,0.07852808433743479,0.08318686118901694,0.0879012183526216,0.0926429046325944],[0.16293386941751936,0.16119350454011983,0.15939040389680742,0.15752829263381807,0.15561076891082384,0.15364098290474526,0.15162126661676628,0.14955272688044643,0.14743482045136092,0.14526493658849476,0.14303801833285512,0.14074625784963896,0.13837890285355164,0.13592220962392643,0.13335957318512645,0.1306718571742273,0.1278379356245352,0.12483544773677205,0.1216417563505887,0.11823509294031465,0.11459586797363393,0.1107081264316844,0.10656113483698648,0.1021510986420041,0.09748302756315429,0.09257279157632332,0.08744944131811024,0.0821579002482657,0.076762160157939,0.07134909179682243,0.0660328312068402,0.060959227699899296,0.056308697789461376,0.05229365668160666,0.049143916867442,0.04707318085793389,0.04622846099153778,0.04664316879485012,0.048225216750894896,0.05079105570124689,0.05412220241118296,0.0580122798975795,0.06229095127333203,0.06682879484368044,0.0715321733160809,0.07633485567678532,0.08118985807256517,0.08606282226816352,0.0909271871470282,0.09576096466088954],[0.16454870804044908,0.1629205670746712,0.16122835499128177,0.1594739591057284,0.15765893051866453,0.15578419577168523,0.1538497339398444,0.15185423138517526,0.14979473138658977,0.147666300653467,0.14546173873685111,0.14317135894586672,0.1407828699949052,0.1382813858767535,0.1356495873133562,0.13286805189969642,0.12991576244281042,0.1267707950499716,0.12341118147695133,0.11981593539025978,0.11596623072504567,0.11184672330825539,0.10744701539795465,0.10276327796925672,0.09780006914699749,0.09257242162713468,0.08710832046743648,0.08145175785496324,0.07566662988691782,0.06984180570677741,0.06409765699092682,0.058593916377839506,0.053537302647272675,0.04918382219853948,0.04582456398772838,0.04373981727852455,0.04311951822682316,0.043987132710491754,0.04618774873756477,0.04945384321695611,0.053494771128115445,0.058056725765723446,0.06294369984614576,0.06801479820596949,0.07317294044999574,0.0783527888520928,0.0835106802838162,0.08861706168774366,0.09365115014441863,0.09859735865837246],[0.16605055498120852,0.164522585146858,0.16292874793936538,0.16126926698582955,0.15954386216432428,0.15775149200318364,0.15589007275417124,0.1539561856898508,0.15194478798469047,0.14984894602977064,0.1476596127701827,0.14536547220939067,0.14295287423874717,0.1404058812246023,0.13770644435269816,0.13483472289595663,0.1317695539160717,0.12848907423675576,0.12497149179171331,0.12119600067830998,0.11714383449227368,0.11279945690307767,0.10815189831497442,0.10319626478627208,0.0979354732425858,0.0923823105164126,0.08656198107721005,0.08051541164862563,0.0743037347630575,0.06801458229672201,0.06177102935128734,0.05574396129849038,0.050167348821578396,0.04535097755231568,0.0416729639590287,0.039518872403986764,0.03914975164955195,0.04056833961185487,0.043513827793466346,0.04759482141074796,0.05243119808909798,0.05772195963951123,0.06325255654491163,0.06887833619288215,0.07450490269968396,0.0800720729367933,0.08554220326431015,0.09089207217634027,0.09610737233861005,0.10117906354737047],[0.16744316506122478,0.16600453751140018,0.16449796344293455,0.16292217514355223,0.16127526819482477,0.15955447201666348,0.15775590558046404,0.15587432890258424,0.15390290381558425,0.1518329800372842,0.1496539244019448,0.14735301198758735,0.144915397545633,0.14232418401861163,0.13956060209603846,0.13660431098049347,0.1334338262793545,0.13002707682755651,0.12636208902638235,0.12241779578075437,0.11817496825454621,0.11361727354764417,0.1087324715555921,0.10351378210655705,0.09796148310466143,0.09208484918895166,0.08590462155839954,0.0794563366889904,0.07279507527702159,0.06600258589857133,0.059198357334295175,0.05255698298834219,0.04633419474290505,0.040899284197635055,0.036750967905647684,0.034447371844885236,0.034376005901368495,0.03649363573296222,0.0403514647084533,0.045376710025523743,0.051088308592429826,0.05714911227099124,0.06334032391798744,0.06952456516283262,0.07561736835753563,0.08156811376158278,0.08734769258846438,0.09294050210972972,0.09833920813227871,0.10354131792013709],[0.16873133937518586,0.167372435562447,0.1659433763019474,0.16444157098204204,0.16286368821778477,0.16120545172203565,0.1594614276791973,0.15762481318733718,0.1556872375069135,0.15363858966236782,0.15146688715810436,0.14915820099136567,0.14669665163433018,0.1440644891800141,0.1412422684923375,0.13820912720045916,0.1349431710953295,0.13142196840022385,0.12762315206432448,0.12352512831613753,0.11910789096773441,0.11435394535484426,0.10924935477046623,0.10378493820585595,0.09795767550306346,0.09177242287897602,0.08524412423117787,0.07840085362078703,0.07128830664792922,0.06397690521931534,0.05657375222436877,0.049243710034056,0.04224713612533829,0.03600318184878881,0.03116538301700575,0.028584892383266818,0.02889700105370492,0.03194663885279821,0.03693269227514354,0.04303098332316812,0.04967238225912771,0.056513536973696654,0.06335369547823637,0.0700758762476832,0.07661264429086773,0.08292661437623236,0.08899897662166331,0.09482243416367053,0.10039668945224621,0.10572549822124074],[0.16992065663200873,0.16863303200597132,0.16727304376278027,0.1658369416673891,0.16432015507868825,0.1627171114187495,0.16102105081930107,0.15922384546151533,0.1573158337530963,0.15528568077202426,0.15312027718439217,0.15080468897788596,0.14832216976001067,0.1456542460457506,0.1427808839905698,0.13968074359701935,0.13633152381341967,0.13271039950360924,0.12879454940948531,0.12456177341969865,0.11999119824660813,0.11506407371733166,0.10976466839376196,0.10408128503564726,0.098007437058023,0.09154326365213425,0.08469732820612697,0.07748907347475482,0.0699524683747498,0.06214194274124864,0.05414298299154988,0.04609281566690286,0.038224072278798975,0.030960878819623755,0.02511061083150347,0.022026092466523553,0.022894753957053912,0.027252294716380545,0.03361324783366706,0.040870225010682125,0.04843783761092512,0.05601887207417842,0.06345656304021233,0.070665754387512,0.07760075232642231,0.0842391149086521,0.09057268550547712,0.09660219551211784,0.10233380177829192,0.10777678126439173],[0.17101723471911334,0.16979356470199844,0.16849543370091144,0.16711808923770302,0.16565589978429568,0.1641021933805176,0.16244909586630607,0.16068737625741483,0.15880630801206772,0.15679355584541746,0.1546350982307119,0.15231519568838744,0.14981641435823126,0.1471197131848753,0.14420460139959124,0.14104937099525539,0.1376314067694139,0.13392757450082957,0.1299146862058643,0.1255700404918005,0.12087203611448734,0.11580085836344975,0.11033924143488817,0.10447331654619074,0.09819356719783419,0.09149593384083089,0.08438314925094667,0.07686646367660206,0.06896808508956821,0.06072504432066246,0.052196165969470056,0.043476542693999545,0.034732458323997774,0.02630002214920551,0.019000681637091666,0.014950995831641405,0.01677582897185931,0.023009027622641308,0.030912571478831155,0.039283941739000156,0.04767249909931334,0.055882771185035394,0.06381846759449603,0.0714298176960015,0.07869248528855784,0.08559753944189757,0.09214589059010428,0.09834480554828012,0.10420554187221998,0.10974167502505405],[0.17202752172931257,0.1708615340466779,0.16961919011489912,0.16829488624230668,0.16688209937531637,0.16537324379138368,0.16375952995273327,0.16203083216643877,0.16017557261330895,0.15818062995516205,0.15603128102288968,0.15371118396461242,0.1512024106673059,0.14848553527325303,0.14553978425893907,0.14234325193849148,0.13887318354360018,0.13510632638799344,0.13101934822616612,0.12658932093666192,0.12179426726062291,0.11661376866159721,0.11102963362394204,0.10502662816109291,0.09859327453021512,0.09172273139757953,0.0844137818584577,0.07667198175645881,0.06851107749968978,0.05995493941412929,0.05104062545879895,0.041824326385760176,0.03239611385357659,0.022928964168197393,0.013918655245588293,0.007969002471488884,0.011734652504022858,0.02026591658401529,0.029491911583994224,0.03869205783863252,0.047661995399938324,0.05631281498558021,0.06459832797359566,0.07249450119096083,0.07999125156903536,0.08708811156049115,0.09379142001961382,0.10011226826071792,0.10606491362210187,0.11166553804938495],[0.17295811532540797,0.17184451211045748,0.17065293351802885,0.16937706897369192,0.1680096644854127,0.16654239574340382,0.1649657453136837,0.16326888981292376,0.16143960365453186,0.1594641864299551,0.15732742117575843,0.1550125706367738,0.1525014181568651,0.14977435903315423,0.14681054711334743,0.14358810018767143,0.14008436644037395,0.13627625300846558,0.13214061667690896,0.12765471603960118,0.12279672417677912,0.11754630112754749,0.11188522625444046,0.10579809212702947,0.09927306404829185,0.09230271341582506,0.08488494022962728,0.07702401393749705,0.06873179218714284,0.060029251485048,0.05094866888039233,0.04153744406747263,0.03186703770521421,0.022063022865261957,0.012471533329755508,0.005682765510138155,0.010950923907840244,0.02031456344322705,0.02995639858042075,0.039440480721251295,0.04863520408601588,0.057475899949137536,0.06592584741135843,0.07396494295149476,0.08158470845133592,0.08878529126717878,0.09557328653382123,0.10196000790432676,0.10796007180432451,0.11359023900361395],[0.17381560908842317,0.17274998168651529,0.17160509394882809,0.17037406570352193,0.16904906388458196,0.1676211907558318,0.16608037776210235,0.16441529027109097,0.16261324902698077,0.16066017450813744,0.15854056052674886,0.15623748330595613,0.1537326519205497,0.15100650541803706,0.14803836120298794,0.14480661845042214,0.14128901951733064,0.13746297166643964,0.1333059310386034,0.12879585086213904,0.1239116965531962,0.11863403189661312,0.1129456833178457,0.10683249413143596,0.1002841891161519,0.09329538506676974,0.08586681230647626,0.07800687236952039,0.06973379033335514,0.061078940878839465,0.052092777522940864,0.04285733593419113,0.03351810532970025,0.02438490127913359,0.016333253712029587,0.012266212950827814,0.015765215195397798,0.02356679083515667,0.03252506003036766,0.04168150694383874,0.050711200531835185,0.05947061723181113,0.06788529241685347,0.07591456250837993,0.08353759573854051,0.09074658040158684,0.09754276051261207,0.10393379682317698,0.10993184997816682,0.11555212142578228],[0.1746064643462097,0.17358520337880495,0.17248377443403531,0.17129485758388777,0.1700101836765399,0.16862043673433588,0.16711516327001755,0.1654826932923939,0.16371007824046435,0.16178305140813748,0.1596860165766065,0.15740207055021127,0.1549130651063579,0.15219971355622214,0.1492417467312986,0.14601812284848906,0.14250729547810342,0.1386875438912637,0.13453737058486753,0.1300359720313437,0.12516379105878603,0.11990316335288613,0.1142390774659427,0.1081600794243377,0.10165937344145648,0.09473620727585334,0.08739770118736392,0.07966142052950569,0.07155929139084947,0.06314413512313902,0.05450173386872484,0.04577558358641029,0.037223108328617985,0.029352720155327874,0.02323280910357437,0.02074473669337722,0.023152771566713047,0.02918045368179954,0.03693189638693348,0.045333174447798455,0.05387779897438671,0.06231419010106154,0.07050680093486983,0.07837891081772277,0.08588717998803908,0.09300902297281927,0.09973559959159341,0.10606750585047729,0.11201189385423055,0.11758042672464208],[0.17533690587284476,0.17435710883816977,0.17329664280242024,0.17214787001405443,0.17090221900689656,0.1695501004814317,0.16808083126015216,0.16648257071692873,0.16474227450077505,0.16284567069017714,0.16077726371498025,0.1585203714729723,0.15605720107079482,0.1533689685789967,0.15043606818013694,0.1472382962082625,0.14375513596669046,0.13996611005863752,0.1358512085392894,0.13139140389440712,0.12656926829125037,0.12136971576382241,0.1157809037792721,0.10979534822685112,0.10341133933588818,0.09663480506465445,0.08948187641187431,0.08198261374455991,0.0741867555611095,0.0661731672154609,0.05806635015998948,0.05006675028750616,0.04250726991999842,0.0359500834950576,0.03128912950265998,0.029604253845548493,0.03141917309100279,0.03614115911316155,0.04267747116250101,0.0501499657169228,0.0580136510074755,0.06594931057906331,0.07376791870454646,0.08135528085768781,0.08864218672019977,0.09558794447463727,0.10217078624450047,0.10838191188443959,0.11422156120804719,0.1196962888474882],[0.17601283976315998,0.17507221822088292,0.17405084975720728,0.17294089230621237,0.17173359616331252,0.17041923283690316,0.16898703305871016,0.16742513808592552,0.1657205688317282,0.16385921769712852,0.16182586824663495,0.15960424808769194,0.15717712051206315,0.15452642069166891,0.15163344257476769,0.14847908321870537,0.145044152287791,0.14130975607253984,0.13725776798915715,0.1328714016092952,0.1281359086585435,0.1230394344290422,0.11757407890338151,0.11173723743107676,0.10553333682063569,0.09897615335695858,0.0920920204310395,0.08492444436949413,0.07754101487672946,0.07004412130351263,0.06258794488174492,0.055405183843034674,0.04884575237151286,0.043417485817736814,0.03977624434706463,0.0385520308982427,0.03999707521713277,0.04379402447871105,0.04928836073077789,0.055832284218899034,0.06293579322275371,0.07026588534654946,0.07760396767739829,0.08480774776575264,0.09178521033209489,0.09847800712697724,0.10485086287924146,0.1108846424743718,0.11657165370006567,0.12191235243438686],[0.1766397917094568,0.1757365798918252,0.17475297107361526,0.17368102342908864,0.17251192284435665,0.17123592432250892,0.1698423035899009,0.1683193228530426,0.16665421506194922,0.16483319140842034,0.16284147713536032,0.16066338107871556,0.15828240474747932,0.155681397232646,0.1528427629148137,0.14974872994207356,0.14638168895715584,0.14272461382469415,0.1387615795229564,0.13447839748329685,0.1298633963510515,0.12490838776462514,0.11960987447845879,0.11397058548941352,0.10800146538229528,0.10172431172227446,0.09517535810744117,0.0884102581363448,0.08151114814666958,0.07459672022348704,0.06783630896223014,0.06146811385847437,0.05581770647642627,0.05130195089955229,0.04838509420820985,0.0474529575626112,0.04864212267080608,0.05176413782184118,0.05640580333963202,0.062101208685797195,0.0684451461035192,0.07512704512208863,0.08192288367240687,0.08867574951587069,0.0952777454978033,0.10165617947381524,0.10776367212537961,0.11357116484120117,0.11906293682251261,0.12423299497994728],[0.17722286383579872,0.17635573032817495,0.17540897170975836,0.17437464149178145,0.17324396418212368,0.1720072888491522,0.17065405388875793,0.16917276682034077,0.1675510033569084,0.16577543040798912,0.1638318580965449,0.1617053263305652,0.15938023201154167,0.1568405036521889,0.1540698311090521,0.1510519594434675,0.147771057789117,0.1442121767814436,0.14036181195613576,0.13620859607412894,0.13174415134399073,0.12696414411220142,0.1218696014141027,0.11646857314015296,0.11077825853255359,0.10482776465704836,0.0986617290456658,0.09234511221874511,0.08596951481236223,0.0796612918246878,0.07359124177851897,0.06798412318806869,0.06312270906814184,0.05933518819315512,0.05695057944946181,0.056217495215009274,0.057216787061584375,0.05982780967803363,0.06377662279400911,0.06872687956518894,0.07435557270240836,0.0803907720831869,0.0866198953724221,0.09288376725051184,0.09906653272902738,0.1050859022891067,0.11088509688458707,0.11642658410786753,0.12168730795972084,0.12665506770037946],[0.1777667081816281,0.17693467210833475,0.17602418952247031,0.17502739448223012,0.17393564186967056,0.17273947267946527,0.17142859145515268,0.16999185961140006,0.16841730881495245,0.16669217904659905,0.16480298644980196,0.16273562661870708,0.160475519634402,0.15800780398796324,0.1553175876208637,0.15239026578804363,0.14921191746860502,0.1457697948323727,0.14205292411298126,0.13805284153810873,0.13376449525493372,0.12918735414342492,0.12432677783083201,0.11919571985181482,0.11381685787778181,0.10822526933793877,0.10247179005450438,0.09662718669834199,0.09078719016579738,0.08507816701040502,0.07966254614453348,0.0747417806761846,0.07055248016536168,0.06734924201126435,0.0653687566797243,0.06477863704841301,0.06563013249971394,0.06784157955457383,0.07122365212776087,0.07553007017812254,0.08050679107747565,0.08592385851204255,0.09158913653063033,0.09735011348531548,0.10308994997974401,0.10872165859877914,0.1141823040714343,0.11942793640763966,0.12442941018606084,0.12916902252050072],[0.17827551487647864,0.17747786780694286,0.1766033361849363,0.17564420962613314,0.1745920535115844,0.1734376854835803,0.17217116494688656,0.17078179924126263,0.1692581705951279,0.1675881884438912,0.16575917221854747,0.16375797030952882,0.16157112162873566,0.15918506708561025,0.15658641943581236,0.15376230145055508,0.15070076431475557,0.14739130074803886,0.14382547074353433,0.1399976622540971,0.13590601484843934,0.1315535414700636,0.1269494918797354,0.12211101043174671,0.11706514832559696,0.11185129097641787,0.1065240427194669,0.1011565494087721,0.0958440892657613,0.09070744918418847,0.08589503270425064,0.0815817714112974,0.0779619454326992,0.07523279012265122,0.07356784471447989,0.07308451266575129,0.07381705809021888,0.07570781530786758,0.07862136476619988,0.08237426905353869,0.08676710361996533,0.09160893335730282,0.09673132756967241,0.10199375056737565,0.10728355519245526,0.1125132885814823,0.11761702821543886,0.12254665568157745,0.12726846979670484,0.13176027092361783],[0.1787530130181246,0.17798924757266185,0.1771505128297779,0.17622931861090918,0.17521750912289283,0.17410625003159702,0.1728860292793323,0.1715466752352788,0.1700773962122947,0.16846684586412417,0.16670321951113148,0.16477438705480207,0.1626680688647786,0.16037206190049777,0.15787452441659422,0.15516432896179813,0.15223149508851802,0.1490677153212683,0.14566699055255594,0.14202639416994847,0.13814698778917311,0.13403491516676375,0.12970270390933955,0.12517080527055385,0.12046939716131366,0.1156404578726062,0.11074007600351604,0.10584087578854899,0.10103427687501888,0.09643203904102282,0.09216614897805264,0.0883856513452719,0.08524876043777184,0.0829090340608121,0.08149616443451922,0.0810950333497203,0.08172953539706099,0.0833575926976941,0.08587957559829441,0.08915652356057402,0.09303130625597153,0.09734675927549977,0.10195799113013995,0.10673890079072162,0.11158434818211657,0.11640962788485955,0.12114854572293486,0.12575094378822727,0.13018015454326956,0.13441062417117708]],"type":"contour"},{"hoverinfo":"text","legendgroup":"In-sample","marker":{"color":"black","opacity":0.5,"symbol":1},"mode":"markers","name":"In-sample","text":["Arm 0_0\u003cbr\u003eaccuracy: 0.452 (SEM: None)\u003cbr\u003eC: 3.42871e-05\u003cbr\u003egamma: 0.000601517","Arm 1_0\u003cbr\u003eaccuracy: 0.536 (SEM: None)\u003cbr\u003eC: 55.3814\u003cbr\u003egamma: 5357.65","Arm 2_0\u003cbr\u003eaccuracy: 0.804 (SEM: None)\u003cbr\u003eC: 690.339\u003cbr\u003egamma: 0.00857996","Arm 3_0\u003cbr\u003eaccuracy: 0.816 (SEM: None)\u003cbr\u003eC: 9319.74\u003cbr\u003egamma: 0.00262294","Arm 4_0\u003cbr\u003eaccuracy: 0.82 (SEM: None)\u003cbr\u003eC: 9422.61\u003cbr\u003egamma: 0.00344744","Arm 5_0\u003cbr\u003eaccuracy: 0.82 (SEM: None)\u003cbr\u003eC: 12400\u003cbr\u003egamma: 0.00644048","Arm 6_0\u003cbr\u003eaccuracy: 0.808 (SEM: None)\u003cbr\u003eC: 11469.7\u003cbr\u003egamma: 0.00712929","Arm 7_0\u003cbr\u003eaccuracy: 0.816 (SEM: None)\u003cbr\u003eC: 7436.44\u003cbr\u003egamma: 0.00124453","Arm 8_0\u003cbr\u003eaccuracy: 0.816 (SEM: None)\u003cbr\u003eC: 40394.4\u003cbr\u003egamma: 0.00133494"],"visible":true,"x":[3.428714353076635e-05,55.38136172368294,690.33938400923,9319.742944380141,9422.61363120716,12399.99246609989,11469.710556154172,7436.440673474601,40394.43106054603],"xaxis":"x","y":[0.0006015170467586964,5357.645905431237,0.008579956814279222,0.002622938701902548,0.0034474437049411173,0.006440480639129858,0.0071292854503499405,0.0012445306696626736,0.0013349353055128505],"yaxis":"y","type":"scatter"},{"hoverinfo":"text","legendgroup":"In-sample","marker":{"color":"black","opacity":0.5,"symbol":1},"mode":"markers","name":"In-sample","showlegend":false,"text":["Arm 0_0\u003cbr\u003eaccuracy: 0.452 (SEM: None)\u003cbr\u003eC: 3.42871e-05\u003cbr\u003egamma: 0.000601517","Arm 1_0\u003cbr\u003eaccuracy: 0.536 (SEM: None)\u003cbr\u003eC: 55.3814\u003cbr\u003egamma: 5357.65","Arm 2_0\u003cbr\u003eaccuracy: 0.804 (SEM: None)\u003cbr\u003eC: 690.339\u003cbr\u003egamma: 0.00857996","Arm 3_0\u003cbr\u003eaccuracy: 0.816 (SEM: None)\u003cbr\u003eC: 9319.74\u003cbr\u003egamma: 0.00262294","Arm 4_0\u003cbr\u003eaccuracy: 0.82 (SEM: None)\u003cbr\u003eC: 9422.61\u003cbr\u003egamma: 0.00344744","Arm 5_0\u003cbr\u003eaccuracy: 0.82 (SEM: None)\u003cbr\u003eC: 12400\u003cbr\u003egamma: 0.00644048","Arm 6_0\u003cbr\u003eaccuracy: 0.808 (SEM: None)\u003cbr\u003eC: 11469.7\u003cbr\u003egamma: 0.00712929","Arm 7_0\u003cbr\u003eaccuracy: 0.816 (SEM: None)\u003cbr\u003eC: 7436.44\u003cbr\u003egamma: 0.00124453","Arm 8_0\u003cbr\u003eaccuracy: 0.816 (SEM: None)\u003cbr\u003eC: 40394.4\u003cbr\u003egamma: 0.00133494"],"visible":true,"x":[3.428714353076635e-05,55.38136172368294,690.33938400923,9319.742944380141,9422.61363120716,12399.99246609989,11469.710556154172,7436.440673474601,40394.43106054603],"xaxis":"x2","y":[0.0006015170467586964,5357.645905431237,0.008579956814279222,0.002622938701902548,0.0034474437049411173,0.006440480639129858,0.0071292854503499405,0.0012445306696626736,0.0013349353055128505],"yaxis":"y2","type":"scatter"}],                        {"annotations":[{"font":{"size":14},"showarrow":false,"text":"Mean","x":0.25,"xanchor":"center","xref":"paper","y":1,"yanchor":"bottom","yref":"paper"},{"font":{"size":14},"showarrow":false,"text":"Standard Error","x":0.8,"xanchor":"center","xref":"paper","y":1,"yanchor":"bottom","yref":"paper"},{"showarrow":false,"text":"x-param:","x":0.26,"xanchor":"left","xref":"paper","y":-0.26,"yanchor":"top","yref":"paper"},{"showarrow":false,"text":"y-param:","x":0.26,"xanchor":"left","xref":"paper","y":-0.4,"yanchor":"top","yref":"paper"}],"autosize":true,"height":450,"hovermode":"closest","legend":{"orientation":"v","x":0,"y":-0.2,"yanchor":"top"},"margin":{"b":100,"l":35,"pad":0,"r":35,"t":35},"title":{"text":"accuracy"},"updatemenus":[{"buttons":[{"args":[{"x":[[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],[3.428714353076635e-05,55.38136172368294,690.33938400923,9319.742944380141,9422.61363120716,12399.99246609989,11469.710556154172,7436.440673474601,40394.43106054603],[3.428714353076635e-05,55.38136172368294,690.33938400923,9319.742944380141,9422.61363120716,12399.99246609989,11469.710556154172,7436.440673474601,40394.43106054603],[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],[3.428714353076635e-05,55.38136172368294,690.33938400923,9319.742944380141,9422.61363120716,12399.99246609989,11469.710556154172,7436.440673474601,40394.43106054603],[3.428714353076635e-05,55.38136172368294,690.33938400923,9319.742944380141,9422.61363120716,12399.99246609989,11469.710556154172,7436.440673474601,40394.43106054603]],"y":[[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],[3.428714353076635e-05,55.38136172368294,690.33938400923,9319.742944380141,9422.61363120716,12399.99246609989,11469.710556154172,7436.440673474601,40394.43106054603],[3.428714353076635e-05,55.38136172368294,690.33938400923,9319.742944380141,9422.61363120716,12399.99246609989,11469.710556154172,7436.440673474601,40394.43106054603],[1e-06,1.757510624854793e-06,3.0888435964774785e-06,5.428675439323859e-06,9.540954763499944e-06,1.67683293681101e-05,2.94705170255181e-05,5.1794746792312125e-05,9.102981779915228e-05,0.00015998587196060574,0.0002811768697974231,0.0004941713361323833,0.000868511373751352,0.0015264179671752333,0.0026826957952797246,0.004714866363457394,0.008286427728546842,0.014563484775012445,0.025595479226995333,0.04498432668969444,0.07906043210907701,0.1389495494373136,0.244205309454865,0.42919342601287785,0.7543120063354607,1.325711365590108,2.329951810515372,4.094915062380427,7.196856730011514,12.648552168552959,22.229964825261955,39.06939937054613,68.66488450042998,120.67926406393264,212.09508879201925,372.7593720314938,655.1285568595496,1151.3953993264481,2023.5896477251556,3556.4803062231213,6250.551925273976,10985.411419875572,19306.977288832455,33932.217718953296,59636.23316594637,104811.3134154683,184206.99693267164,323745.754281764,568986.6029018281,1000000.0],[1e-06,1.757510624854793e-06,3.0888435964774785e-06,5.428675439323859e-06,9.540954763499944e-06,1.67683293681101e-05,2.94705170255181e-05,5.1794746792312125e-05,9.102981779915228e-05,0.00015998587196060574,0.0002811768697974231,0.0004941713361323833,0.000868511373751352,0.0015264179671752333,0.0026826957952797246,0.004714866363457394,0.008286427728546842,0.014563484775012445,0.025595479226995333,0.04498432668969444,0.07906043210907701,0.1389495494373136,0.244205309454865,0.42919342601287785,0.7543120063354607,1.325711365590108,2.329951810515372,4.094915062380427,7.196856730011514,12.648552168552959,22.229964825261955,39.06939937054613,68.66488450042998,120.67926406393264,212.09508879201925,372.7593720314938,655.1285568595496,1151.3953993264481,2023.5896477251556,3556.4803062231213,6250.551925273976,10985.411419875572,19306.977288832455,33932.217718953296,59636.23316594637,104811.3134154683,184206.99693267164,323745.754281764,568986.6029018281,1000000.0],[0.0006015170467586964,5357.645905431237,0.008579956814279222,0.002622938701902548,0.0034474437049411173,0.006440480639129858,0.0071292854503499405,0.0012445306696626736,0.0013349353055128505],[0.0006015170467586964,5357.645905431237,0.008579956814279222,0.002622938701902548,0.0034474437049411173,0.006440480639129858,0.0071292854503499405,0.0012445306696626736,0.0013349353055128505]],"z":[[[0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608,0.4773149851920608],[0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391,0.4758524463825391],[0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978,0.4745758561746978],[0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826,0.47350515375011826],[0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374,0.47265992663449374],[0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166,0.47205910396994166],[0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334,0.471720627838334],[0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203,0.47166110882344203],[0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362,0.4718954736163362],[0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559,0.4724366139993559],[0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325,0.4732950478746325],[0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687,0.47447860401186687],[0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752,0.4759921427602752],[0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146,0.47783732500329146],[0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353,0.48001244106616353],[0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915,0.48251231009314915],[0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985,0.4853282586181985],[0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785,0.4884481847312785],[0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907,0.49185671149579907],[0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239,0.4955354302186239],[0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425,0.49946323091941425],[0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739,0.503616713959739],[0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754,0.5079706732842754],[0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072,0.5124986380318072],[0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196,0.5171734552502196],[0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605,0.5219678918868605],[0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827,0.5268552288698827],[0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297,0.5318098136944297],[0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205,0.5368075302984205],[0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394,0.5418261361735394],[0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786,0.5468454070835786],[0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408,0.5518470210144408],[0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381,0.5568141093563381],[0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963,0.5617304162493963],[0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405,0.5665790648162405],[0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636,0.5713410851939636],[0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073,0.5759941413515073],[0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011,0.5805121090770011],[0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922,0.58486588767922],[0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074,0.5890251423406074],[0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626,0.592960296737626],[0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515,0.5966442601269515],[0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258,0.6000536811562258],[0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513,0.6031697148970513],[0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975,0.6059783716458975],[0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322,0.6084705404996322],[0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001,0.6106417800235001],[0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955,0.6124919567867955],[0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815,0.614024796715815],[0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121,0.6152473977042121]],[[0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134,0.1685196913897134],[0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337,0.1671478746014337],[0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875,0.16570628078776875],[0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584,0.16419253234943584],[0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833,0.16260352675712833],[0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873,0.16093522831902873],[0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496,0.15918245050496],[0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615,0.15733863857313615],[0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948,0.15539566452613948],[0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976,0.15334364833716976],[0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152,0.15117082069447152],[0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931,0.1488634429959931],[0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088,0.14640579983885088],[0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586,0.1437802777450586],[0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057,0.1409675414365057],[0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814,0.13794681585630814],[0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846,0.13469627871060846],[0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182,0.1311935650758182],[0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791,0.12741638317695791],[0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541,0.12334323947072541],[0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915,0.11895427244969915],[0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282,0.11423219912708282],[0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167,0.10916338743777167],[0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072,0.10373908424381072],[0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023,0.09795685664403023],[0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397,0.09182235207577397],[0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555,0.08535156607276555],[0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852,0.07857395651328852],[0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027,0.07153702127147027],[0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813,0.06431348367160813],[0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956,0.057013233131253956],[0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385,0.04980397971114385],[0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265,0.04294716009892265],[0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274,0.03685535514706274],[0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039,0.03215407982000039],[0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801,0.02963285375825801],[0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017,0.0298710147203017],[0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547,0.03274069430028547],[0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157,0.03751798543933157],[0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274,0.04342599006913274],[0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351,0.04990761233740351],[0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335,0.056617424376972335],[0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857,0.06334976817220857],[0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817,0.06998327731502817],[0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244,0.07644719191969244],[0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302,0.08270168809965302],[0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773,0.08872613501837773],[0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501,0.0945118140988501],[0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758,0.10005725378032758],[0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045,0.10536518680233045]],[],[],[[0.44356211245639093,0.44145510641767405,0.4397124084771437,0.4383856244660861,0.4375281042215909,0.4371942775592792,0.4374388212293931,0.4383156442188362,0.43987668602204655,0.44217053398973577,0.4452408823615758,0.4491248771840477,0.4538514166799558,0.45943950228412267,0.46589675556980775,0.4732182232321127,0.48138557978866253,0.490366803929847,0.5001163548332744,0.5105758208666457,0.5216749683577385,0.5333330921018006,0.5454605644884766,0.5579604925284258,0.570730414275556,0.5836639908250008,0.596652671843845,0.6095873284653768,0.6223598562347304,0.6348647526824222,0.6470006696856165,0.6586719310752813,0.6697899923358658,0.6802748036098392,0.6900560221585129,0.6990740093276737,0.7072805438784346,0.714639192095982,0.721125297809415,0.7267255917156484,0.7314374640632857,0.7352679879476646,0.7382328096183558,0.7403550265043425,0.7416641495289135,0.7421952006058776,0.7419879445982838,0.7410862150372367,0.7395372759560787,0.737391169147833],[0.44035889816806517,0.43812252784846883,0.43625748603630965,0.4348179008032389,0.43385997810674287,0.43344134256349215,0.4336201950456623,0.43445426869418163,0.4359995712655206,0.43830891292070445,0.44143023611235277,0.4454047890998474,0.45026521625857197,0.45603367324943767,0.46272010573447964,0.47032084557884773,0.4788176672799241,0.48817740484011646,0.4983521621864869,0.5092800763984909,0.5208865336003285,0.5330857066586211,0.5457822837854058,0.5588732796674001,0.5722498538937992,0.5857990949380981,0.5994057554013206,0.6129539429345712,0.6263287808439433,0.6394180535316183,0.652113845660251,0.6643141713342948,0.6759245719521916,0.6868596405020684,0.697044408702423,0.7064155155562687,0.7149220668809724,0.7225261010575512,0.7292026013992188,0.7349390413003037,0.7397345093386711,0.7435985244530888,0.7465496969475889,0.7486144009386763,0.7498255899934588,0.7502218196633166,0.7498464635666011,0.7487470524910631,0.7469746464335997,0.7445831666537271],[0.43733011950293416,0.4349679088469291,0.4329832125502215,0.43143256193596335,0.43037490886264024,0.42987097972038785,0.42998243401674596,0.4307708029737075,0.4322961882826139,0.4346157111203151,0.4377817190340652,0.4418397856251997,0.44682657608060683,0.45276769796126975,0.45967570248361617,0.4675484308464903,0.47636789394627777,0.48609982067558644,0.49669391766631144,0.5080847799920691,0.5201933124923411,0.532928486465587,0.5461892661205849,0.559866577478261,0.5738452403392704,0.5880058277224847,0.6022264502225629,0.616384483561348,0.6303582672143982,0.6440288019920607,0.6572814662202467,0.6700077547071119,0.6821070229282665,0.6934881922226688,0.704071342849818,0.7137890949767937,0.7225876597581108,0.7304274421751242,0.7372831026799918,0.7431430406280713,0.7480083448829342,0.7518913488690345,0.7548139997173003,0.7568062724248837,0.7579048130580143,0.7581518924501397,0.7575946348464431,0.7562844032801878,0.7542762032639178,0.7516280028678008],[0.4345027228735361,0.4320200765115368,0.4299203093591274,0.42826220384942704,0.4271073059271893,0.426519300160184,0.4265631798478158,0.4273041814086212,0.42880645482320806,0.4311314495312676,0.4343360110498581,0.43847021158957755,0.4435749816073031,0.4496796686611358,0.4567997167052668,0.46493471145707993,0.47406704374329384,0.4841613777907156,0.49516498195993336,0.5070088311532845,0.5196092815351457,0.5328700818116492,0.5466845135812294,0.5609375155918446,0.5755077136111761,0.5902693322605487,0.6050940025703267,0.6198525004670656,0.6344164600121749,0.6486601036753277,0.6624620218666339,0.6757070160562921,0.6882879943421624,0.7001078758837088,0.7110814231336092,0.7211368826916623,0.7302172848364764,0.7382812400680453,0.7453030920785358,0.7512723514919118,0.756192443713378,0.7600789378297339,0.7629575393029442,0.7648621734189837,0.7658334231998706,0.7659174288645183,0.7651651747367003,0.7636319685919567,0.7613769032174947,0.758462162506296],[0.4319030899352518,0.4293073892074243,0.4270991552732322,0.42533923969853477,0.42409159135187946,0.4234226591665728,0.4234005834396956,0.42409413937651047,0.4255713964125167,0.4278980610913038,0.4311354835832803,0.4353383337967994,0.4405519993843079,0.4468098300987409,0.45413044665398267,0.4625154216717379,0.4719476738142373,0.482390840975059,0.49378971300396035,0.5060715853659937,0.5191482461072688,0.5329182786839086,0.5472694259194731,0.562080857822971,0.5772252750621877,0.5925708437715337,0.6079829962464197,0.6233261518744824,0.638465419097948,0.6532683359439588,0.6676066952899016,0.6813584816309597,0.6944099179624502,0.7066575838209901,0.7180105191681887,0.7283921772328563,0.7377420411682447,0.7460166893550589,0.7531901030559407,0.7592530791288785,0.7642117497862243,0.7680854032396224,0.7709039849277356,0.7727057486722615,0.7735354461429782,0.7734432007397736,0.7724839249355919,0.7707169610846587,0.7682056294696299,0.7650165065907649],[0.429556467668892,0.4268571102475899,0.4245491030283398,0.42269516018749953,0.4213614079311587,0.4206168192753539,0.4205324341359153,0.42118032394870286,0.42263225711362773,0.4249580217733406,0.42822336938533556,0.43248756267726934,0.4378005552939261,0.4441999109123105,0.4517076936718473,0.4603277069116829,0.4700435460992254,0.48081785592009413,0.4925929099030482,0.5052922955503314,0.5188232829043735,0.5330794516217976,0.5479432756428799,0.5632885098163763,0.5789823335694027,0.5948872745326669,0.6108629706452567,0.6267678447188002,0.6424607687725259,0.6578027906758989,0.6726589838937385,0.6869004616578076,0.700406567759936,0.7130672150723933,0.7247852884318929,0.735478962250314,0.7450837128150799,0.75355374795891,0.7608625611434218,0.7670023789002142,0.7719824387947579,0.7758263038766784,0.7785687162264663,0.7802526704428938,0.7809272958030017,0.7806467564799876,0.7794699121520527,0.7774602128379348,0.7746853574985749,0.7712165076337342],[0.42748636015133623,0.424694729512416,0.4222977265830509,0.4203597039434391,0.41894871252499344,0.41813597000342695,0.41799511411495244,0.4186011970495716,0.42002937176610505,0.4223532173248268,0.42564265097858656,0.42996138587475446,0.43536392705128246,0.4418921765656289,0.4495718679732401,0.45840927132080783,0.4683888049809097,0.47947214579596265,0.4915990219703568,0.5046893370428736,0.518645995097164,0.5333578695151118,0.5487025846720752,0.5645489813636775,0.580759260116124,0.5971908584273643,0.6136981446912736,0.6301340205203819,0.6463515231746539,0.6622055142242566,0.6775545297326648,0.6922628494792034,0.7062028149238718,0.719257383628295,0.7313228475590636,0.7423115622415739,0.7521544376984074,0.7608028476884949,0.7682295566696966,0.7744282985376408,0.779411826326965,0.7832086128471178,0.7858588470064867,0.7874107178556773,0.787917905299943,0.7874385970561573,0.7860355677188814,0.7837764484528686,0.7807334994311489,0.7769826813054694],[0.4257139038319208,0.4228432569144799,0.4203700247789355,0.41835996410570275,0.4168827799713492,0.4160116264752907,0.4158223938962955,0.4163927368930794,0.4178007912982505,0.4201235202014906,0.42343462490247463,0.42780195715873365,0.43328438664746066,0.43992813716356755,0.44776275759027995,0.4567971966476175,0.4670168340140146,0.47838239574967056,0.4908310610883336,0.5042791651161279,0.518625546056931,0.5337548398799236,0.5495404073066233,0.5658468249540761,0.5825319863924597,0.5994489025309286,0.616447304460224,0.6333751539825565,0.6500801645184047,0.6664114298020675,0.6822212491607823,0.6973672238857386,0.7117146752438842,0.725139395272486,0.7375306794608866,0.7487944989992803,0.7588565479543538,0.7676647603745245,0.7751907733825675,0.7814297891248534,0.786398461143019,0.7901308823958426,0.7926734527488013,0.7940800615494846,0.7944090597461433,0.7937225477915585,0.7920871429558196,0.7895747672337713,0.7862624827207175,0.7822312802382161],[0.4242572538719812,0.42132251932560755,0.4187876171119816,0.4167194706985515,0.4151891600195546,0.4142714502903662,0.4140441098641773,0.41458697109093706,0.4159806803213864,0.41830507455596916,0.42163711329415954,0.426048286718287,0.4316014214303437,0.4383468320634228,0.44631788124331145,0.4555263527809819,0.4659587116086211,0.4775747468503121,0.4903091488140665,0.5040749573675308,0.5187674510328485,0.5342676971053476,0.5504455459046315,0.5671620919623169,0.5842716992816772,0.6016237055795852,0.6190639217163136,0.6364360397067488,0.6535830591881711,0.670348838327745,0.6865798697255076,0.7021273723980808,0.7168497731176557,0.7306156174091024,0.7433068924016254,0.7548226479307648,0.7650826578092504,0.7740306720984416,0.7816366093847368,0.7878969175667878,0.792832442465506,0.79648365220842,0.7989040505523928,0.8001537999850494,0.8002959716509999,0.7993963640230287,0.7975253666362673,0.7947594001419093,0.7911806491705183,0.7868753465236034],[0.42313101357554006,0.4201484990725754,0.4175679766446687,0.415457301426623,0.4138886477991525,0.41293806041332176,0.4126847966744676,0.41321041465237884,0.41459755229038836,0.416928334485666,0.42028233405877985,0.424734001071541,0.4303494638842485,0.4371826020336629,0.4452703320445299,0.45462730592607503,0.4652411708791397,0.4770708108363538,0.49004863504275104,0.5040849184521689,0.5190721442079611,0.534888680816119,0.5514017613650737,0.5684698750364172,0.5859447011667904,0.6036727132727091,0.621496574714558,0.6392564429840518,0.6567912965041647,0.6739403958766714,0.6905449895428117,0.7064503696775349,0.7215083739239169,0.7355804054214262,0.7485409958722221,0.7602818461351757,0.7707161229242867,0.7797825513202348,0.787448539886331,0.7937113111394417,0.7985959958986113,0.8021501491353726,0.8044353858123331,0.805518798043217,0.8054681413130488,0.8043526160625212,0.8022464170427598,0.7992308537049905,0.7953936140553535,0.7908262643161258],[0.42234574114271467,0.41933275596282205,0.4167237514514727,0.4145872836518658,0.41299634398584806,0.4120279254629806,0.4117623820182417,0.41228253506818774,0.4136724732434078,0.41601598184309746,0.41939452768442576,0.4238847124961096,0.4295550937040868,0.43646225577672654,0.4446460036478474,0.45412361440110904,0.4648839538556128,0.47688512214049505,0.4900577709092756,0.5043102999329108,0.5195334185714491,0.5356038181894012,0.5523870896167369,0.5697400360483624,0.587512521334725,0.6055489836320068,0.623689737043151,0.6417721792546791,0.6596320209982037,0.6771046529852461,0.6940267669854707,0.7102383484475941,0.7255851555779147,0.7399217883224035,0.7531154189972684,0.7650501834586655,0.77563208269652,0.78479397403575,0.792499816663352,0.798746870047584,0.8035643281614346,0.8070073190355981,0.8091465821002349,0.8100568797297286,0.8098105450091515,0.8084799242807788,0.8061433513012188,0.8028876504915435,0.7988063123810887,0.7939960067681845],[0.4219075670185115,0.4188819746389178,0.4162622273163633,0.41411735426271384,0.4125208892518029,0.4115504446229568,0.411287079068382,0.4118144133187861,0.41321743970421715,0.4155809621456023,0.4189875922387665,0.42351521451159796,0.42923381942184796,0.43620158593875896,0.4444600763025449,0.4540283843195019,0.4648964473325901,0.4770220281525193,0.49033507960372635,0.5047433553430895,0.5201369679197909,0.5363920124232506,0.553373426889832,0.5709372432080848,0.5889323684650615,0.6072020262888181,0.6255849805274551,0.6439166593529413,0.6620302963836932,0.6797582064294027,0.6969333165652243,0.7133910776383375,0.7289718852791174,0.7435241392046551,0.7569080564497838,0.7690003089539936,0.77969943797662,0.7889317314852113,0.7966567383697017,0.802870844215137,0.8076067594907261,0.8109271982695134,0.8129126989852589,0.8136464198312685,0.8132052059120397,0.8116647146152961,0.8091083186530132,0.8056290588153585,0.8013260703923965,0.7963003006264373],[0.4218179504535048,0.41879767392929684,0.4161849790322551,0.41404913908546576,0.4124639539578842,0.4115073243970435,0.4112606197375772,0.411807792981134,0.41323418908316883,0.4156249828349958,0.4190631718069731,0.4236270372059928,0.4293869709546783,0.436401550554361,0.4447127241897928,0.45433995446637904,0.4652736764936174,0.47747243242303056,0.49086695954223064,0.5053657146205178,0.5208594102879296,0.5372246134280487,0.5543265746588439,0.5720214420605788,0.5901579985966913,0.608579052339889,0.6271226014969553,0.6456228921531524,0.6639114854914862,0.6818184528583555,0.6991738212885821,0.7158093986756786,0.731561115979125,0.746272031911181,0.7597961487218734,0.7720031733391673,0.7827842921799278,0.7920588230206554,0.7997810746590078,0.8059456594989777,0.8105881957787036,0.8137785394944349,0.8156066754779223,0.8161643528263661,0.8155333255181454,0.8137940305077463,0.8110363051380651,0.8073594589144779,0.802867091280068,0.7976628569460126],[0.4220735956048114,0.41907610465818784,0.41648774511360453,0.41437779817324627,0.41282004558661783,0.41189233678185855,0.4116759479032343,0.41225468649324126,0.4137136873633916,0.4161378357221445,0.4196097427048475,0.4242071859425091,0.42999991380451885,0.43704569797002407,0.4453855174573023,0.45503788065011713,0.46599324965096833,0.47821184387933285,0.4916265584382379,0.506147859353026,0.521668226932641,0.5380657416102855,0.5552069062114202,0.5729488469581019,0.5911410304154435,0.6096266247955207,0.6282436272941272,0.6468258752184946,0.6652040576445807,0.6832068461954736,0.7006622682292807,0.7173994532321168,0.7332508934169484,0.7480553720102935,0.7616617259999322,0.7739336192563876,0.7847554897151182,0.794039739042315,0.8017348412629087,0.807832789373698,0.8123717463537693,0.8154286018188293,0.8171013695799173,0.8174886438442226,0.816678982908204,0.8147610293869596,0.8118317957547111,0.8079950494441779,0.8033565043843505,0.7980205175701462],[0.4226665363660785,0.4197083480840792,0.4171605422293745,0.4150921591216436,0.41357666447485614,0.41269150180165576,0.41251743428065635,0.4131376295123381,0.4146364324359005,0.4170977623743775,0.4206030597832569,0.4252286973873757,0.4310427615962151,0.4381011143095712,0.44644270926063473,0.45608443742381155,0.46701665638154666,0.47920149934451944,0.4925748276721669,0.5070501829028753,0.5225228793112572,0.5388735021063635,0.5559707146505328,0.5736734593548012,0.5918326728972243,0.610292639026309,0.6288920988887851,0.6474652360544108,0.6658426528413728,0.6838524566265956,0.7013215797089852,0.7180774640743921,0.7339502531898383,0.7487756468355731,0.7623985919650007,0.7746780020806248,0.785492716233499,0.7947489081988393,0.8023890274916534,0.8084014557835355,0.8128263108080679,0.8157479925436559,0.8172725189661589,0.8175035388306041,0.816538441109464,0.8144763386151102,0.8114194693319889,0.8074727125278608,0.8027413218059891,0.7973286043002024],[0.42358438653742014,0.4206806107448007,0.4181880140373338,0.41617513161841935,0.41471479902826813,0.4138836827259778,0.4137615970877572,0.414430561167326,0.41597354078880067,0.41847281314120816,0.42200788282908114,0.4266528728237749,0.4324733185362399,0.4395223306952952,0.4478362231611397,0.4574300412501006,0.46829400003491006,0.480392121958786,0.49366352833970695,0.5080254949422291,0.5233770009098939,0.5396019999885927,0.556572153673459,0.5741490165948595,0.592185754364805,0.610528500888407,0.6290174685411141,0.6474879257872916,0.6657711579290777,0.683695529526387,0.7010877722964193,0.7177746302936496,0.7335850051008999,0.7483527578525727,0.7619203424500655,0.7741434656992384,0.7848969957668757,0.7940823704295832,0.8016367838001416,0.8075442658988625,0.8118454501127389,0.8146315316774911,0.8160181931035163,0.8161193670198158,0.8150404047152231,0.8128850747190616,0.8097566486797745,0.8057587086837688,0.8009944837732849,0.7955651787702914],[0.4248107396869994,0.42197469554761646,0.41954998813058747,0.41760436847252375,0.4162097137303689,0.4154415300721534,0.41537823910972477,0.41610020186935104,0.4176884275678763,0.420222908219312,0.4237805163468441,0.4284324067219352,0.43424088566829167,0.4412557782243598,0.4495104783523177,0.45901814655773954,0.4697688350245012,0.48172834358478694,0.4948390638521968,0.5090223024076789,0.5241812397859302,0.5402038642973813,0.5569655500939518,0.574331185628766,0.5921568796702218,0.6102913241486205,0.6285769137208873,0.6468507302998705,0.6649455054882084,0.6826906785438017,0.6999136737659472,0.7164415297687771,0.732103024429384,0.7467314537264558,0.7601682406712035,0.7722675727787727,0.7829022943144917,0.7919713155869899,0.7994088525743989,0.8051958934699244,0.8093725814460363,0.8120342553604889,0.8133051351270657,0.8133135144280019,0.8121720617945535,0.8099811590891719,0.806841258454553,0.8028532908795619,0.7981176664940012,0.7927328385013269],[0.42632569280542376,0.4235686158971657,0.4212221980918175,0.4193531168066029,0.41803195527788717,0.41733267401990576,0.4173318641916216,0.4181077387458003,0.4197388123726048,0.422302218407731,0.4258716131805044,0.4305146320853894,0.43628989896136516,0.44324367040010115,0.4514063393434735,0.4607892181775234,0.4713821769820538,0.48315265225440873,0.49604618185410554,0.5099881589433042,0.5248862432025159,0.5406329094615498,0.5571078049620574,0.5741797717030268,0.5917085131836404,0.6095459524294168,0.6275373621381137,0.6455223648330606,0.6633359107744581,0.6808093491003984,0.6977717157857651,0.7140513718356454,0.7294781374643899,0.7438860835204645,0.7571171609489414,0.769025874061112,0.7794852365471455,0.7883942961117043,0.7956875829669545,0.801346821386106,0.805412315479422,0.8079795101397885,0.8091763594024171,0.8091372951054525,0.8079802742711524,0.805805515252843,0.8027093315228334,0.7987884910529095,0.7941395440644606,0.7888574026859472],[0.42810646084967274,0.4254373112121551,0.42317711757214105,0.42139119127589547,0.42014848876577937,0.41952105065036754,0.4195832233458281,0.42041062251901085,0.42207879521119196,0.42466153871931184,0.42822884273364553,0.4328444431547347,0.43856302087111854,0.44542715714745523,0.45346427172989917,0.46268389542755084,0.4730756965428409,0.4846086025553375,0.49723111684860555,0.5108726365474043,0.5254453913776199,0.5408466094522902,0.5569606184914699,0.5736607219773167,0.5908107967232121,0.6082666293952885,0.625877052052628,0.6434849615992673,0.6609283235818934,0.6780412723711868,0.694655430572338,0.7106015823682384,0.7257118496217285,0.7398225369989642,0.7527778343638376,0.7644345929067901,0.7746684273368404,0.7833814333294058,0.7905117693993561,0.7960446493208464,0.8000206319724673,0.8025316763512877,0.803702336636406,0.8036649200798667,0.802538897639061,0.8004268077919865,0.7974230537119364,0.7936202342870986,0.7891103626288538,0.7839840640548255],[0.4301280460675463,0.42755341897768034,0.4253848505247807,0.42368599959797953,0.4225238769288277,0.42196825378170266,0.42209085691404913,0.42296431375990473,0.4246608121870261,0.42725044424204395,0.4307992165593569,0.4353667366161241,0.4410036296012177,0.4477488087767283,0.45562680676070877,0.46464545120850426,0.4747941910366519,0.48604330640844845,0.4983440695743442,0.5116297296442487,0.5258170592968746,0.5408081688837441,0.556492344648162,0.5727477553078344,0.5894429565383887,0.6064381890082898,0.6235865112100553,0.6407348384743141,0.6577249801294328,0.6743947824402743,0.6905794989231676,0.7061135239867686,0.720832642002154,0.7345769628484936,0.747194737116017,0.758547267690076,0.7685151481338844,0.777006011178707,0.7839636598048634,0.7893772656665631,0.7932865931628234,0.7957774360064682,0.7969659107572082,0.7969773893615908,0.7959292182546401,0.7939249671000059,0.7910585105265956,0.7874194063670223,0.7830953715116062,0.7781724902827989],[0.43236392643742155,0.42988806009957,0.4278140253060083,0.42620355745974103,0.4251214273475023,0.42463482411244174,0.42481253148632747,0.42572386692010167,0.427437356197621,0.4300191242465141,0.4335309990641101,0.43802835334063994,0.443557750127589,0.4501545138441735,0.4578404072488204,0.4666216388327696,0.47648742606829647,0.4874092783055607,0.4993410463454083,0.5122196532718923,0.5259663227403595,0.5404880854006523,0.555679367126345,0.5714235193511183,0.5875942164726334,0.6040567024128216,0.6206689128179619,0.6372825320332128,0.6537440681935626,0.6698960489620535,0.6855784573402429,0.7006305434456209,0.7148931651994275,0.72821182832149,0.7404406111217422,0.7514471623535669,0.7611189201028621,0.7693705294209849,0.7761519296802464,0.7814554414766608,0.7853186136228545,0.787819375202137,0.789063084956768,0.7891656332732921,0.7882392601618796,0.7863861342114926,0.783699194696234,0.7802656280622103,0.7761694328278751,0.7714923445597938],[0.43478673096482146,0.43241159962399855,0.4304326484117268,0.42890944190170915,0.4279042501968596,0.42748141283496255,0.4277065060188688,0.4286452889224872,0.43036240980776347,0.43291986279980804,0.43637520346468534,0.44077955765593296,0.44617549386001604,0.4525948715051367,0.4600568179210296,0.4685660105022933,0.4781114319914663,0.4886657168120759,0.5001851226660059,0.5126100687357016,0.5258661095772663,0.5398651812592397,0.554506964381253,0.5696802446009157,0.5852641990202321,0.6011295840182368,0.6171398407695595,0.6331521674545346,0.6490186332960769,0.6645874311071316,0.6797043838532263,0.6942148379308002,0.707966091285264,0.7208105157005021,0.7326095322673067,0.7432385689093954,0.752593027131275,0.7605950282242205,0.7672001749387931,0.7724027195069156,0.7762367806714373,0.778771619680396,0.7801011229581676,0.7803305059447265,0.7795647793863496,0.7779023548745168,0.77543392169854,0.7722441336516802,0.7684135869598901,0.7640199629079326],[0.43736887497834714,0.4350943524093784,0.43320888399356844,0.43176964641133336,0.43083618804650264,0.4304697816504002,0.43073259291295696,0.43168664672149704,0.433392579261745,0.4359081751506986,0.4392867057445432,0.443575108301562,0.4488120749416231,0.45502615177750166,0.4622339751572222,0.47043878383310395,0.47962933371249855,0.489779302031759,0.5008472067247479,0.5127768001800239,0.5254978430207162,0.5389271358152926,0.5529696872420304,0.5675199199116723,0.5824628498665965,0.5976752138509684,0.6130265542076276,0.6283803023944102,0.6435949284813711,0.6585252463913804,0.6730239838475545,0.6869437419448505,0.7001394802155294,0.7124716640545364,0.7238101914484136,0.7340391533100517,0.7430623377794414,0.7508091093299474,0.757239842481008,0.76234955492544,0.7661681154321994,0.7687559260078353,0.770195467358449,0.7705808730814149,0.7700085805721362,0.7685713660261294,0.7663561601809572,0.7634443807640929,0.7599131263020973,0.7558361701680248],[0.4400831349615126,0.43790721170708274,0.4361117361258876,0.4347513147394039,0.43388259637119436,0.4335636217832933,0.4338530035878857,0.43480892377175645,0.4364879432976688,0.43894362934400216,0.44222502142246956,0.4463749777741187,0.4514284666488799,0.4574108899548781,0.46433654390280055,0.47220732614567756,0.4810117861887157,0.4907245843625973,0.5013063794290656,0.5127041162831028,0.5248516451422734,0.5376705808041623,0.551071307732459,0.5649540509776765,0.5792099582691093,0.5937221688627593,0.6083668753151309,0.6230144127167686,0.6375304350726336,0.6517772602313899,0.6656154827243259,0.6789059668000132,0.6915123365647358,0.7033040697480436,0.7141602640220931,0.72397406028696,0.7326575493233031,0.7401467345282907,0.7464057906120259,0.7514295596318136,0.7552432014564578,0.7578984191879884,0.7594667042421407,0.7600311457625368,0.7596788604650268,0.7584956471649659,0.7565633315982638,0.753959193238688,0.7507564363556689,0.7470248607670156],[0.4429031489888047,0.44082218674026846,0.43911162075915144,0.43782334239511317,0.43701096731154804,0.43672919005030003,0.4370329842683479,0.43797664082887977,0.4396126432731485,0.44199039075381114,0.4451547924272489,0.44914477405490155,0.4539917555720035,0.45971817477386717,0.4663361430544451,0.4738463200523311,0.48223708211849514,0.49148403467533663,0.5015498846069759,0.512384652787723,0.5239261765997077,0.5361008338592792,0.5488244154155075,0.5620030826007382,0.5755343641566497,0.5893081710430992,0.6032078331000377,0.6171111864441339,0.6308917633007496,0.6444201557239373,0.6575656401255643,0.6701981584514863,0.6821907499601911,0.6934225076277994,0.7037820841587338,0.7131716800354039,0.7215112967210159,0.728742832573657,0.7348333749304895,0.7397768975224822,0.7435936554810881,0.7463269913665019,0.7480379637919653,0.748798898189541,0.7486872636982876,0.7477810085506821,0.7461557980099667,0.7438838997523471,0.7410340906623085,0.7376719685082916],[0.44580383488283876,0.44381284256172426,0.4421808226629541,0.44095684423064346,0.4401913994886631,0.43993577057177424,0.44024125767153816,0.44115826481011017,0.4427352466172741,0.44501752913334436,0.448046029654476,0.45185591426219934,0.4564752454462544,0.46192368383159854,0.4682113145936965,0.47533766794353094,0.48329099244123785,0.49204782027251054,0.5015728378719811,0.5118190482051056,0.5227281879668606,0.5342313481736116,0.5462497421558417,0.5586955704605681,0.5714729455677071,0.5844788578053945,0.5976041847215241,0.6107347672852518,0.6237525960384723,0.6365371672670689,0.6489670816215302,0.660921962559865,0.6722847649778032,0.6829445187173467,0.6927994986561725,0.7017607242024491,0.7097555631261442,0.7167310600577642,0.7226564688907945,0.7275244136522002,0.7313502190106008,0.734169280538701,0.7360328196163942,0.7370028055359349,0.7371470160028473,0.7365350455466263,0.7352356496437069,0.7333153545736238,0.7308379711356345,0.7278645865838299],[0.44876172340029763,0.44685464136725433,0.4452938391709497,0.4441254934432949,0.44339692364943434,0.4431559772287197,0.44345029168470107,0.4443264330539432,0.44582891689953996,0.44799912654203405,0.45087415335913034,0.4544855949013147,0.45885835698786254,0.4640095140784829,0.46994728604008146,0.47667018718593834,0.48416639428997305,0.49241336473731806,0.5013777162251483,0.5110153588362141,0.5212718525681403,0.532082951541076,0.5433752917612524,0.5550671825455007,0.5670694713093587,0.5792864655066445,0.5916169120701585,0.6039550519258363,0.6161917834479789,0.6282159825029077,0.6399160359924299,0.6511816476529451,0.661905965068717,0.671988049844399,0.6813356625860331,0.689868256700929,0.6975199727469622,0.7042423141739869,0.7100061003723261,0.7148022840470148,0.7186413338254518,0.7215511296595317,0.7235736422003007,0.7247609519247965,0.725171286702596,0.7248656621924738,0.723905448772758,0.7223508877562663,0.7202603604606076,0.7176901294339543],[0.4517552079227672,0.449925188951854,0.4484276172432693,0.44730574198300493,0.44660369820766965,0.4463659154807352,0.44663641843144386,0.4474580210540609,0.44887142278431114,0.4509142218172422,0.45361986953753686,0.4570165985882301,0.4611263649323511,0.465963849910746,0.4715355703566145,0.47783914217434953,0.4848627350012329,0.4925847432174728,0.5009736832745928,0.5099883114617064,0.5195779424221371,0.5296829391434544,0.5402353410503367,0.5511595984475489,0.5623733881940611,0.5737884958676662,0.5853117623088835,0.5968461058348431,0.6082916441710392,0.6195469507695484,0.6305104868117452,0.6410822502724776,0.651165673448366,0.6606697760436979,0.6695115382117874,0.6776183953699624,0.6849306789076434,0.6914037491445552,0.6970095159124086,0.7017370513873964,0.7055920950236422,0.7085954299253091,0.7107803317595318,0.7121894814522336,0.7128718182159173,0.7128797574929706,0.7122670373228354,0.7110872587028738,0.7093930254371069,0.7072355073963125],[0.4547647152633988,0.45300439320560554,0.4515616934848853,0.45047693517328136,0.44979109100273956,0.44954522357483173,0.4497798274476353,0.4505340808154028,0.4518450159541969,0.45374662398059684,0.4562689163801755,0.4594369725783557,0.46327000868437446,0.4677805064299359,0.47297344226710847,0.47884565387860445,0.4853853748068503,0.4925719580433616,0.5003757974536991,0.5087584435599324,0.5176728993082136,0.5270640735836383,0.5368693663729287,0.5470193598673065,0.5574385940314696,0.5680464123653948,0.578757872648781,0.5894847272244087,0.6001364867021071,0.6106215886553619,0.6208486975188314,0.6307281615911683,0.6401736452625634,0.6491039362281515,0.6574448956410981,0.665131473057059,0.6721096516450273,0.6783381341795747,0.6837895465419188,0.6884509459006811,0.6923234912150127,0.6954212603493609,0.6977693512866238,0.6994015366667757,0.700357805188953,0.7006820992973487,0.7004204608692531,0.699619667222801,0.6983263250795535,0.6965863198934256],[0.4577728043870706,0.45607454363057964,0.4546782485940156,0.453621334766734,0.45294166440222444,0.45267701319877046,0.4528644558064296,0.45353967515417903,0.4547362053811435,0.4564846235499303,0.45881171095758444,0.46173961020571763,0.4652850085651685,0.46945838082547325,0.4742633250769204,0.4796960222893829,0.485744845078446,0.49239013312609153,0.4996041432630412,0.5073511724614581,0.5155878432504598,0.5242635344840398,0.5333209366883287,0.5426967106126056,0.552322229845105,0.5621243928091918,0.5720264953096897,0.5819491611845056,0.5918113347099917,0.601531343445883,0.611028043407793,0.6202220588534905,0.6290371251629711,0.6374015332641126,0.6452496553650203,0.652523502617337,0.659174226916023,0.6651634383269279,0.6704641806783197,0.6750614085395735,0.6789518524229421,0.6821432444701351,0.6846529842700091,0.686506420978934,0.6877349818896307,0.6883743731624874,0.6884630223412518,0.6880408490375247,0.6871483692326571,0.6858260815674916],[0.46076420121577444,0.4591203220280333,0.45776208855782513,0.45672406504740765,0.4560410806929765,0.4557477287830336,0.4558777964689307,0.45646363100589016,0.45753545245786154,0.45912062738779275,0.46124292263321737,0.4639217624522563,0.46717151558799425,0.4710008405902402,0.47541211758350316,0.4804009923020062,0.48595605364354705,0.4920586595861493,0.49868291874693005,0.5057958270393106,0.5133575517473266,0.5213218496943476,0.5296366025631176,0.5382444509883093,0.5470835096018731,0.5560881473013624,0.5651898200187532,0.5743179465669759,0.5834008212268527,0.5923665593196973,0.6011440740550311,0.6096640845725664,0.6178601562644201,0.6256697743241939,0.6330354476744237,0.6399058290834688,0.6462368148076396,0.6519925543135044,0.6571462668893235,0.661680744379778,0.6655884345832705,0.6688710528730676,0.6715387475653732,0.673608922061727,0.6751048681355523,0.6760543755427426,0.6764884551958824,0.6764402611721388,0.6759442403029241,0.6750354929457949],[0.46372577840384366,0.46212875496303124,0.4608005650262995,0.45977299627551066,0.45907794388681306,0.45874694329327903,0.4588106442280224,0.4592982323924685,0.4602368086670685,0.4616507395625019,0.4635609963175993,0.46598450332568725,0.4689335190052338,0.4724150734201282,0.47643048657408893,0.4809749891809461,0.4860374638936287,0.49160031974881385,0.4976395064594714,0.504124668813241,0.5110194354843701,0.5182818316127735,0.5258648009103736,0.5337168209226721,0.5417825942384824,0.5500037985322758,0.5583198788650817,0.5666688662168462,0.5749882065273276,0.5832155847195041,0.5912897289614327,0.5991511830889023,0.606743041246738,0.614011649224802,0.6209072897697692,0.6273848778091138,0.6334046855790312,0.6389330890151245,0.6439432796669995,0.6484158414988762,0.6523390760698896,0.6557089869670486,0.6585288962938557,0.660808737464621,0.6625641235583228,0.663815314051262,0.6645861940774888,0.6649033492764678,0.664795279795539,0.6642917614482738],[0.4666464891665157,0.4650891185449322,0.46378344689667594,0.4627585789879091,0.4620435928650292,0.461667106721715,0.461656796567292,0.462038871290043,0.4628375147614852,0.4640743077729014,0.46576764559535927,0.46793216951965655,0.47057823254896863,0.4737114201878344,0.4773321467695372,0.4814353458834334,0.4860102702582799,0.49104041215309885,0.4965035502789663,0.5023719239907427,0.5086125304230287,0.5151875357957925,0.5220547885220947,0.5291684190550692,0.5364795094539578,0.543936814110503,0.5514875115647153,0.5590779655174063,0.5666544709270777,0.5741639588787184,0.5815546329870297,0.5887765128382919,0.5957818698506944,0.602525561311082,0.6089652992393937,0.6150619236706165,0.6207797652768761,0.6260871573649806,0.6309570877243336,0.6353678957049048,0.639303866852196,0.6427555853531439,0.6457199640719021,0.6481999496090444,0.6502039638541707,0.651745177810943,0.6528407173690843,0.6535108827273926,0.6537784348568655,0.6536679738599527],[0.46951726406086663,0.4679928056201877,0.46670275440045084,0.4656736415992261,0.4649318593748482,0.4645032617388049,0.4644127247010348,0.46468367231921137,0.46533757789924896,0.46639345220490236,0.46786733296077,0.4697717919440138,0.47211547731446146,0.47490270931157086,0.478133146889914,0.4818015412061002,0.4858975891603354,0.49040589660809764,0.495306056666308,0.5005728440772228,0.506176522194246,0.5120832550836993,0.5182556136425678,0.5246531615083321,0.5312331037211495,0.5379509783019643,0.5447613677863732,0.5516186040153022,0.5584774350874213,0.5652936188252795,0.5720244038995574,0.5786288610211164,0.5850680376399211,0.5913049373244307,0.597304374185681,0.6030328163302587,0.6084583801643157,0.6135511217403984,0.6182836681344104,0.6226320850180085,0.6265767751710846,0.6301031997241339,0.6332022887626745,0.6358705048076799,0.6381095994947841,0.6399261457413882,0.6413309380815928,0.6423383428221486,0.6429656579789618,0.6432325192225317],[0.47233087916068334,0.47083316478097187,0.4695525660321017,0.468513162521283,0.467738802889194,0.4672527392043961,0.4670772280671863,0.46723310499243226,0.4677393408417158,0.46861259123899696,0.46986675186687865,0.4715125341180842,0.4735570765835898,0.47600360813188064,0.47885117775874525,0.4820944649211275,0.48572368175518293,0.48972457554693727,0.4940785362723802,0.4987628101871426,0.5037508165516283,0.5090125607997853,0.5145151338784122,0.5202232840606548,0.5261000441098016,0.5321073929732744,0.5382069269046561,0.5443605097673454,0.5505308661848374,0.5566820745610177,0.5627799111554501,0.5687919945602216,0.5746876884619079,0.5804377502627857,0.5860137771427303,0.5913876020307183,0.5965308930427609,0.601415221379894,0.6060127115981204,0.6102971403505861,0.6142451808018542,0.6178374936064243,0.6210594823473976,0.6239016605985055,0.6263596670445549,0.6284340090322592,0.6301296257246349,0.6314553530981366,0.6324233547045235,0.6330485615820978],[0.47508180342528245,0.4736053197432969,0.4723288075873404,0.47127402672167606,0.47046243282506717,0.46991484451940246,0.46965108365109626,0.4696895952148479,0.4700470551703453,0.47073797619436614,0.47177432299839805,0.4731651500788837,0.47491627550975507,0.4770300045127087,0.47950491596582767,0.48233572370693767,0.485513222487816,0.4890243258333167,0.4928521999963716,0.49697649483828144,0.5013736689560123,0.5060174028326585,0.5108790902385063,0.5159283945007007,0.5211338524349887,0.5264635044557844,0.5318855243652789,0.537368816296639,0.5428835391043152,0.5484015103326837,0.5538964336586435,0.5593438878870792,0.5647210181086164,0.5700058933346575,0.5751765631786707,0.5802099845964677,0.5850811756986894,0.5897630368298821,0.5942270648318941,0.5984447613514285,0.6023892696181004,0.6060368263172786,0.6093678152519733,0.612367378780895,0.6150256362406937,0.6173375957074377,0.6193028512240013,0.6209251476605695,0.6222118786307667,0.6231735646714728],[0.4777660323062721,0.47630597671194175,0.47502903145633174,0.4739547753355637,0.4731024271339937,0.4724905441588467,0.4721366997413343,0.4720571458463178,0.47226646850308174,0.47277724525200865,0.47359971508522425,0.474741472326343,0.47620719643366666,0.47799842972858697,0.4801134144839654,0.48254699963415515,0.48529062561273795,0.4883323935524979,0.49165722239183884,0.495247094432827,0.499081386686741,0.5031372819862916,0.5073902503450588,0.5118145873389587,0.5163839922321374,0.5210721639661549,0.5258533877302692,0.5307030783848052,0.5355982393347407,0.5405177865389844,0.5454426775911824,0.5503557765868925,0.5552413806777894,0.5600843445570817,0.5648687929815865,0.5695765679809802,0.5741858607087863,0.5786707332456502,0.5830019565131981,0.5871488310880969,0.5910812544653358,0.5947714995433355,0.598195503137405,0.601333659676645,0.6041711929166699,0.6066981998223575,0.6089094587518916,0.6108040822555865,0.6123850791796511,0.6136588745997119],[0.48038091381878223,0.4789332263780982,0.4776521931906344,0.47655535566715934,0.47565985485954415,0.4749821601820379,0.474537782064397,0.4743409743870231,0.47440443387096287,0.4747390048199077,0.47535339864614506,0.47625393836386093,0.4774443386130115,0.4789255317121653,0.48069554968062594,0.4827494711004814,0.48507944012289966,0.48767476290435763,0.4905220843526758,0.49360564534112117,0.496907617571999,0.5004085100706825,0.504087637855064,0.5079236395879426,0.5118950268604399,0.5159807430037067,0.5201607037839665,0.5244162857969035,0.5287307206690526,0.5330893442079109,0.537479639505192,0.5418910021555954,0.5463141457278433,0.5507400616431364,0.5551584698108678,0.5595558202325611,0.5639133129774868,0.5682060242661666,0.5724039562378608,0.5764743955916868,0.5803844085471918,0.5841028699867079,0.587601910791485,0.590857837514126,0.5938516186212219,0.5965690346381785,0.5990005813152669,0.601141202380393,0.6029899142585742,0.6045493709778043],[0.48292497246454014,0.4814863462260051,0.4801984312637533,0.47907687769437696,0.4781369089184212,0.47739307907323575,0.4768590187114959,0.4765471742362451,0.47646854773480773,0.4766324448626191,0.4770462392588621,0.4777151625529398,0.4786421292734474,0.47982760584170037,0.48126953228042335,0.4829633042781771,0.48490182182867103,0.4870756088385524,0.48947300590880044,0.4920804359868257,0.49488273979280295,0.4978635748551568,0.5010058686243068,0.5042923124085342,0.5077058786889442,0.5112303395856789,0.5148507587083349,0.5185539221714811,0.5223286670565925,0.5261660569702662,0.5300593445819539,0.5340036502385701,0.5379952742827596,0.5420305495950062,0.5461041354500484,0.5502066943772217,0.55432225686524,0.5584267978171829,0.5624896308951484,0.5664764073312101,0.5703519403433288,0.5740823744491854,0.5776367251091197,0.5809878867930549,0.5841132106923481,0.5869947460984908,0.5896192292120612,0.5919778913102536,0.5940661456963694,0.5958832005430642],[0.48539773556220245,0.4839656078827686,0.48266885489512423,0.4815213820370722,0.48053665411256374,0.4797274799290765,0.47910578885369,0.47868240448441124,0.4784668215645321,0.4784669930955919,0.4786891352666771,0.4791375582522122,0.47981453107975436,0.48072018858650883,0.48185248793492874,0.4832072212276687,0.4847780894506728,0.48655684129501686,0.48853347838633027,0.49069652610899855,0.49303336656559615,0.4955306272574067,0.49817461578117395,0.5009517871534037,0.5038492262106455,0.5068551227833799,0.5099592118808992,0.513153144835796,0.5164307501405536,0.5197881345048551,0.5232235654652226,0.5267370667468587,0.5303296466336965,0.5340020680212663,0.5377530568624757,0.541576835527286,0.5454599894533436,0.5493793615291802,0.5533039204315784,0.5571983116940745,0.5610258160734541,0.5647505754041668,0.5683391939602754,0.5717618203813175,0.5749928072692286,0.5780110366269974,0.5807999893880285,0.5833476265943871,0.5856461387652282,0.5876916092062281],[0.48779956573648775,0.48637209334909753,0.4850653438205342,0.48389162327584556,0.4828627942245818,0.4819900857773326,0.4812838989374963,0.4807536118242036,0.48040739045947695,0.48025201142784646,0.48029270323811546,0.4805330135331154,0.48097470935721076,0.4816177174631776,0.48246011109120696,0.4834981487665453,0.48472636943381964,0.4861377466804616,0.48772390290892387,0.4894753821069456,0.49138197733898104,0.4934331062281076,0.49561822448551507,0.4979272639220623,0.5003510772711441,0.5028818674763414,0.5055135737559955,0.5082421806586868,0.5110659093944381,0.5139852429211539,0.5170027275782871,0.520122484526506,0.5233493539465566,0.5266875839659411,0.5301389647003961,0.5337002956636229,0.5373601239265625,0.5410963853172174,0.5448784330766216,0.5486707117051304,0.5524357443622318,0.5561364024411333,0.5597375668569159,0.563207281841573,0.566517493343772,0.5696444551493701,0.5725688764083344,0.5752758744603835,0.5777547869636277,0.5799988877142285],[0.4901315025569368,0.4887075231100134,0.48739036297735916,0.4861908715206467,0.4851194609907013,0.4841859406852258,0.4833993488593217,0.4827677869039611,0.48229826095241346,0.4819965366203467,0.48186701298826,0.48191262215201547,0.4821347606589378,0.4825332588791335,0.48310639380896375,0.48385094994838984,0.48476233172780464,0.4858347294805804,0.487061339165578,0.4884346339387152,0.4899466832475388,0.49158951235984133,0.49335549210513274,0.4952377450590513,0.49723055037395614,0.4993297248821468,0.501532952895004,0.5038400312198031,0.5062529892567986,0.5087760365844126,0.5114152821797673,0.5141781603756076,0.5170724888871764,0.5201050739625532,0.5232797682925034,0.5265948958449883,0.5300402216161195,0.5335951358495441,0.5372302186217252,0.5409105374650188,0.5445986258590718,0.548256799987841,0.551848883410174,0.5553414337451065,0.5587045591032602,0.5619124033239951,0.5649433700462815,0.5677801465051513,0.5704095788966189,0.5728224424343444],[0.4923951156096389,0.4909740983520734,0.489646794236743,0.4884227342298663,0.4873110267858136,0.4863202142948486,0.48545812953345147,0.48473175629555715,0.48414709891378394,0.4837090658149278,0.4834213725562853,0.4832864699223818,0.4833055025913096,0.4834783035766925,0.48380342909155294,0.4842782376464386,0.484899016074481,0.4856611537628845,0.48655936465796795,0.4875879545913818,0.48874112913595613,0.49001333451961215,0.49139962107319407,0.49289601522011506,0.4944998820792949,0.4962102562879509,0.4980281135951385,0.49995655007330675,0.5020008293985115,0.504168251540533,0.506467788410961,0.5089094236961348,0.5115031258537215,0.5142573776316127,0.5171771950872397,0.5202616593263716,0.523501399611922,0.5268773339523446,0.5303617879372019,0.5339211649602782,0.5375187339516888,0.5411169466554837,0.5446792156558146,0.5481712116761783,0.5515617570392753,0.5548233891122393,0.5579326602141355,0.5608702322213542,0.5636208158215794,0.5661729963835251],[0.4945923706382478,0.49317435881258553,0.4918377865607172,0.4905909994741048,0.489441941996034,0.4883980345097853,0.4874660522968381,0.4866520102130046,0.4859610573625836,0.4853973863905692,0.48496416222916006,0.48466347519535435,0.48449632321219416,0.4844626275906127,0.4845612862398025,0.4847902673538521,0.48514674553687265,0.4856272809670503,0.4862280405510834,0.4869450580720257,0.4877745280691954,0.4887131255853021,0.48975834094280535,0.490908815329894,0.49216465914108803,0.49352773068001876,0.4950018479458155,0.4965929007561025,0.49830882440485846,0.5001593894812174,0.5021557556405503,0.5043097308084762,0.5066326739646403,0.5091339872650307,0.511819187582382,0.5146876992375111,0.5177308675687073,0.5209310808812778,0.524262588802394,0.5276935910668511,0.5311886848906382,0.5347110796714287,0.5382243839108563,0.5416939553617631,0.5450878640456124,0.5483775304472345,0.5515380996228847,0.554548606110534,0.5573919775079418,0.5600549174525002],[0.4967255098085732,0.49531105716031226,0.4939666252927634,0.4926995011257824,0.49151659729667635,0.49042434825256387,0.4894286097379446,0.488534565203212,0.48774664300607035,0.48706844853554854,0.48650271552977636,0.48605128085664584,0.48571508685449366,0.48549421496466005,0.4853879538077959,0.48539490404367097,0.4855131212940747,0.4857402970869142,0.4860739761826003,0.48651180675630445,0.48705181771291467,0.487692714882275,0.48843418495222485,0.48927719271311837,0.4902242534750402,0.4912796583463836,0.49244962541246873,0.4937423447432506,0.4951678796892273,0.4967378813830913,0.49846506849827865,0.5003624220195791,0.5024420498640235,0.5047137005115403,0.5071829743663259,0.5098494357868383,0.51270506532072,0.5157336321959857,0.518911313788222,0.5222083275254888,0.525591002576714,0.5290238047859811,0.5324710686116803,0.5358983641752377,0.5392735110141595,0.5425672812450115,0.5457538428270329,0.548810992399642,0.551720222498725,0.554466662162924],[0.4987969466364728,0.4973870502577362,0.4960366207065025,0.49475200583726886,0.4935392103992381,0.4924038095195819,0.4913508668006211,0.4903848602436896,0.48950961948353633,0.4887282780030976,0.48804324407507943,0.487456194119663,0.48696809195365803,0.486579237013449,0.4862893440427163,0.4860976559278712,0.48600309032361577,0.4860044194224438,0.4861004806699887,0.4862904143962421,0.4865739222020338,0.48695153748933834,0.4874248967296399,0.4879969969032282,0.488672420996097,0.4894575095073436,0.4903604516319496,0.4913912652510819,0.49256163035585226,0.4938845366650775,0.49537370432337213,0.4970427395909864,0.4989040013896052,0.5009671907971949,0.503237750819691,0.5057152877248937,0.508392361880117,0.5112540283749643,0.5142783201318346,0.5174375355863725,0.5206999646749896,0.5240316834654722,0.5273981765007748,0.53076567810238,0.534102209011549,0.5373783275916245,0.5405676323221776,0.5436470570028239,0.5465969988293063,0.5494013157027922],[0.5008091756728861,0.4994052071828505,0.4980510154392259,0.49675212114633743,0.4955137362800349,0.49434069338006503,0.4932373804008053,0.4922076840299795,0.4912549445901694,0.49038192576104783,0.48959080238007374,0.4888831694740206,0.48826007542222755,0.4877220817346191,0.4872693513247089,0.48690176635253446,0.4866190756881267,0.48642107078739466,0.48630778726297297,0.48627972765684674,0.48633809886236723,0.48648505528382824,0.486723936147373,0.4870594823794261,0.4874980151556651,0.48804755463489047,0.4887178536330372,0.48952031729368983,0.4904677766454867,0.49157408223835297,0.4928534856133229,0.4943197844845717,0.495985227783291,0.4978592170347451,0.49994690764319594,0.5022479015907192,0.5047552953156934,0.5074553366998,0.5103278109136434,0.5133470693222237,0.5164834606766487,0.5197048917957703,0.5229783075890663,0.5262709697589498,0.5295514862584557,0.5327905890873952,0.5359616817535566,0.539041187815543,0.5420087344429867,0.5448472035833798],[0.5027646966622232,0.5013683334925708,0.500012910023744,0.4987032236173929,0.49744379945535877,0.4962388340989361,0.49509214530592405,0.49400713072245706,0.4929867382135705,0.49203345066458337,0.4911492880553434,0.49033582946175447,0.48959425735456485,0.48892542612563855,0.4883299561593055,0.4878083539639495,0.48736115787114076,0.48698910758098396,0.48669333436830275,0.4864755670509279,0.4863383468460861,0.48628524199450385,0.4863210505125379,0.4864519766529682,0.48668576365602406,0.4870317622461767,0.4875009112634046,0.4881056041624704,0.4888594135133092,0.4897766462239833,0.4908717068999298,0.49215825855391554,0.493648192889564,0.495350460615141,0.4972698658037126,0.49940598630478283,0.5017524171621912,0.5042965104690361,0.5070196893843657,0.5098982803997504,0.5129047010269846,0.5160088028961106,0.5191791970373594,0.5223844447568917,0.525594053631575,0.5287792598583845,0.5319136040909769,0.534973321638855,0.537937573727451,0.5407885476706531],[0.5046659525794452,0.5032791108884459,0.5019252054012661,0.5006084055877507,0.49933264652099346,0.49810158520861453,0.49691856366346454,0.49578658104898765,0.4947082773302652,0.4936859308816377,0.49272147242828634,0.4918165175147639,0.49097241938082364,0.49019034366680947,0.4894713657512163,0.48881659072611944,0.4882272950273947,0.487705087542451,0.48725208660633984,0.48687110765766,0.4865658544527648,0.48634110463151575,0.4862028781047774,0.48615857423032904,0.4862170611376539,0.4863886979987455,0.48668526878116375,0.48711980450543324,0.4877062709970107,0.48845910173859275,0.4893925624210636,0.4905199474525741,0.4918526314157316,0.49339903133856555,0.495163575593546,0.4971458116802906,0.499339799696743,0.5017339126423345,0.5043110958417751,0.5070495476394419,0.509923708311924,0.5129054099886052,0.5159650487264176,0.5190726740624623,0.5221989320455837,0.5253158326647026,0.528397337458385,0.5314197784397194,0.5343621276019903,0.5372061395649118],[0.5065152807044504,0.5051400511951498,0.5037905610461665,0.5024704388365567,0.5011831169238923,0.4999317991079031,0.49871943532279767,0.4975487054233071,0.49642201418044657,0.49534149958059226,0.4943090564105542,0.49332637689552516,0.49239500982086726,0.4915164390966821,0.49069218210172527,0.48992390735614527,0.489213570108218,0.4885635632678097,0.4879768797699488,0.4874572809016965,0.4870094633764838,0.48663921600627635,0.4863535547353724,0.486160822623484,0.4860707392122099,0.48609438176791725,0.48624407947595716,0.48653320125376653,0.4869758191915052,0.48758623376792226,0.48837835528630963,0.48936494990807405,0.4905567792322169,0.49196168891706343,0.4935837303706565,0.49542242155461924,0.49747225682413126,0.49972255220081685,0.5021576623108824,0.5047575425472056,0.5074985760990062,0.5103545565863138,0.5132977164245837,0.5162997107781896,0.519332495284934,0.5223690633117486,0.5253840305107628,0.5283540697135984,0.5312582085275546,0.5340780068361934]],[[0.1421214828079791,0.1385712299070121,0.13491828039321857,0.1311949068870602,0.12744083538353906,0.12370356679782728,0.12003827802866289,0.11650708980441951,0.1131774588437035,0.11011946523552449,0.10740185916685621,0.10508693755953825,0.10322464325839834,0.10184665423993035,0.10096151643121631,0.10055189601284834,0.1005746835504139,0.10096404590032303,0.10163683580317577,0.10249931001113781,0.1034540186671912,0.1044059624429833,0.10526750065798943,0.10596186415348087,0.10642538571663035,0.10660869152961319,0.10647712842436054,0.10601067432701551,0.10520352620870091,0.10406350103373477,0.10261132933089805,0.10087986978312175,0.09891322528026629,0.09676569525395057,0.09450045838978,0.09218785294829586,0.08990312580401266,0.08772357840214852,0.08572516638718794,0.08397880487907634,0.08254684402182352,0.08148031091220793,0.08081745175594146,0.08058380262291713,0.08079355366569468,0.08145156037372821,0.08255521422399902,0.08409559094770777,0.0860577276387863,0.08842030716077375],[0.13953996802909555,0.13569042112148264,0.13171278558755334,0.12763995764332103,0.12351344903951106,0.11938410212394197,0.11531242771167467,0.11136829774990038,0.10762964671366466,0.10417979277865178,0.10110304219248877,0.09847846461563312,0.09637217629020355,0.09482909494052144,0.09386572091324968,0.09346570661716574,0.09357952591262525,0.09412850719775145,0.09501230080581438,0.09611807424363192,0.09732964874805984,0.09853527389641897,0.09963342526043127,0.10053659282933804,0.10117337276970441,0.10148929898759068,0.10144683353186316,0.10102485350004373,0.10021787693625217,0.09903518467262876,0.09749992487557665,0.09564822880705623,0.09352831336531545,0.09119949249606468,0.08873096421265322,0.08620019020472966,0.08369066160614047,0.08128888265400462,0.07908054427397442,0.07714612086190355,0.07555645967335478,0.07436920130450785,0.07362686793257016,0.07335704859766687,0.07357439277001841,0.07428344538424707,0.07548111932762551,0.07715795548092653,0.07929804367247033,0.08187814647145003],[0.13701611080687426,0.1328618966310257,0.1285506416732265,0.1241149538436767,0.11959714817410665,0.11505044477917079,0.11053990121496308,0.10614277364673623,0.10194785673821039,0.09805321036352785,0.09456162303991145,0.09157332928052336,0.08917605556216843,0.08743346925171733,0.08637427996361029,0.08598493554853733,0.08620835777679683,0.0869493914376508,0.08808545334172024,0.08947947816782931,0.09099225440142515,0.09249226197426913,0.0938623715233857,0.0950036703339158,0.0958370961142561,0.09630361190345946,0.09636352788074325,0.09599540205341135,0.09519479751545963,0.09397305839901793,0.0923561857610559,0.09038383587255873,0.0881084125652501,0.08559417000643621,0.08291617482844689,0.0801588993096516,0.07741415110572641,0.07477803752115617,0.07234678595093591,0.0702115631141021,0.06845294042878708,0.06713615972190946,0.06630851147426012,0.0659996282227905,0.06622437622736248,0.0669868815920032,0.06828381038955168,0.0701056419770483,0.07243590696310233,0.07524941332213472],[0.13458823025374042,0.13012910257502497,0.12548070102288877,0.12067423179305996,0.11575150746222697,0.11076668632042899,0.10578794200278432,0.10089876438631414,0.09619837534132131,0.09180045824810361,0.08782912397268193,0.08441097650518213,0.08166266155953751,0.07967473138411363,0.07849489823083584,0.07811564426512818,0.07847094557655347,0.07944381650681046,0.08088211504426047,0.08261739286932274,0.08448186518667401,0.08632079272714446,0.08799987329785514,0.08940859332621018,0.09046087125922918,0.09109415387913233,0.09126778351089082,0.09096113859303016,0.0901718240528562,0.08891404683834817,0.08721723063804826,0.08512487581700161,0.08269363305268956,0.07999251257518179,0.07710207946962837,0.07411338170764474,0.07112623441220901,0.06824639415426452,0.0655812094403776,0.06323367301630332,0.06129550691823045,0.059840803848521425,0.05892226732874911,0.05857154415206336,0.05880339850201421,0.05962148613247039,0.06102272050579327,0.06299833071599573,0.06553185870395392,0.06859600108635508],[0.1322976646947466,0.1275396658938724,0.12255750691845978,0.11737974018403075,0.1120460883256162,0.10660971985568782,0.10113973386951122,0.09572363645350047,0.09046932603237386,0.08550566483191602,0.08098010198763547,0.07705122926375325,0.07387419358737955,0.07157857429520519,0.07024229005723326,0.06986984858179598,0.07038461212069375,0.07163951553713904,0.07344172868918471,0.07558123397869947,0.07785458186152582,0.08008013512592478,0.08210541380188173,0.08380896842664128,0.08509919411738268,0.08591179105506416,0.08620686322499255,0.08596614782519024,0.08519057816699095,0.0838982376843538,0.08212270101774798,0.07991173713585414,0.07732633937271557,0.07444002389083136,0.07133827779368122,0.06811791918930386,0.06488594723935719,0.061757250047008994,0.0588504343458947,0.056281293206276596,0.05415430633643161,0.052554029394937966,0.05153948588890077,0.05114432239671436,0.051382808789377246,0.052258220056228856,0.05376865748770784,0.055907400758610074,0.058658722861695455,0.061992692638937176],[0.13018770389309745,0.12514425364689064,0.1198401508587495,0.11430002453634037,0.10855976392328279,0.10266922894589714,0.09669549666624562,0.09072660250061486,0.08487549747354563,0.07928342511621544,0.07412095165339457,0.0695834190333545,0.06587622573873456,0.06318607397502098,0.061640218731173375,0.06126680663807822,0.06197676718135213,0.06357940589547963,0.06582343349572324,0.06844243982610496,0.0711885143141902,0.07384986217163239,0.07625618503881854,0.07827724943875725,0.07981865506889532,0.08081701530518254,0.08123552047553698,0.08106019096512473,0.08029683357773332,0.07896861451642953,0.0771141516207234,0.07478605326572152,0.07204986259279546,0.06898338116378645,0.06567631847023131,0.06223010598756035,0.058757487915010814,0.055381150803445044,0.052230292491291824,0.04943399853685504,0.047111169355380164,0.04535890892269679,0.04424391844335873,0.043801934499354135,0.044046302092762155,0.04498031332988994,0.04660494695443274,0.04891749644132675,0.0519036408249175,0.0555294560385923],[0.12830213456322406,0.12299490330613831,0.1173904191795515,0.11150828278468859,0.10537888106829596,0.09904631850071192,0.09257218226448302,0.08604035040451331,0.0795629648521035,0.07328731679331638,0.06740233504199097,0.06214099683724939,0.05777095598734357,0.05456212766358386,0.05272483481819196,0.05233480486102391,0.05328922965382657,0.05532968016109595,0.05811635038745994,0.06130467054380798,0.06459239457748248,0.06773639598085235,0.07055173357779423,0.07290390358961825,0.07470005519155946,0.0758813491251418,0.07641691897410767,0.07629926451674149,0.07554075707956308,0.0741709626015876,0.0722345648119491,0.06978975586245366,0.06690704159486824,0.06366847344936079,0.06016734674625541,0.0565083493061023,0.052807929499140684,0.0491941969095271,0.045804981048241385,0.04278208098662197,0.04026016365146661,0.03835149344283578,0.03713256561897507,0.03664161234000041,0.03689070365144481,0.03788418936207836,0.03962885468643333,0.04212873613419416,0.045370954696042735,0.04931445668819678],[0.12668342116978512,0.12114281787431481,0.11527016438031774,0.10907931811633516,0.10259389698263424,0.09585012907223935,0.08890069981939358,0.0818200471785309,0.07471172503715326,0.06771853379766747,0.06103567759142723,0.05492501540341876,0.04972188295802731,0.045812670255047316,0.043551200906742776,0.04311410817451054,0.04438682802147631,0.046995611359145525,0.05045795875620846,0.05432010786444111,0.05821780931614976,0.061881267847872456,0.06511919277204992,0.06780063337654547,0.06984041284680145,0.07118866716731174,0.07182357970984617,0.07174632087537004,0.07097743342401497,0.06955414217160219,0.06752825253620613,0.06496444535172735,0.06193889601556849,0.05853825769751201,0.05485914539719403,0.05100829900089281,0.047103489388303776,0.04327479014976971,0.03966488319175183,0.03642568158272966,0.03370776022339258,0.03164146651933152,0.030316412603125807,0.029774516031140886,0.030026636495344643,0.031080546394440856,0.03295375311064473,0.03566024403885604,0.0391864738380648,0.04347783129066266],[0.12537060543657058,0.11963570574522413,0.11353795174112147,0.10708535653812988,0.1002942721550739,0.09319184782882735,0.08581943119336422,0.07823747159593111,0.07053288776136897,0.06283053109664681,0.055311307007736635,0.048239968460264654,0.04200161417552243,0.03712436644108946,0.03420908733218548,0.0336632976308146,0.03537782170327621,0.038755680741463704,0.043068157703508074,0.047714954837429074,0.05227523398625081,0.056470092241995166,0.06011790283003957,0.06310264474409372,0.06535412819235598,0.06683595744968779,0.06753809034741627,0.06747206250701686,0.06666774174347911,0.06517094220591566,0.06304149586051284,0.060351548270053595,0.05718397843233086,0.05363097833391327,0.049792986409399005,0.04577833521622683,0.04170405892008263,0.03769808494578358,0.033902096175575054,0.030472260580208632,0.027572213250073155,0.025352579213341792,0.02392106933018452,0.023326261927098454,0.0235791834498499,0.02469613812701187,0.026713182233101682,0.029656259139797383,0.03350359229556634,0.038175510756460265],[0.12439707833787383,0.11851485477378157,0.11224519945391152,0.10559094482183036,0.09856174511671505,0.09117594687234853,0.0834631399661671,0.07546784735076105,0.06725524582452794,0.058920734653376966,0.05060718694370652,0.0425380464189397,0.03508217395754538,0.02886745112377654,0.024872239464119525,0.024078407565282553,0.026473276670050328,0.03094200132399988,0.03631149971663712,0.0418249703838524,0.047050388204280674,0.05173838333585759,0.05574037980425857,0.058967845684190535,0.06137190183431553,0.06293261483474102,0.06365301580937614,0.06355550891813747,0.06267950532408946,0.06107965299510539,0.05882428735533614,0.0559938637972191,0.05267923294969569,0.04897973751496001,0.045001289894144335,0.040854862357065626,0.03665616001304274,0.032527465919292335,0.028602220508722104,0.02503080097293718,0.02198117288961761,0.019622678824207766,0.01808745533323573,0.017437492303276087,0.017689092493649364,0.018877931614742684,0.02106945533524311,0.024296513153816687,0.028510350327116556,0.03359006661196872],[0.12378844206758695,0.11781224026712163,0.11143222031122421,0.10464746817673048,0.09746265577331609,0.08988934517480093,0.08194763991230977,0.07366840292405007,0.06509650092828036,0.056296115287867085,0.047360688025031766,0.0384345291681957,0.029767624197223064,0.02187589627485627,0.01600996868302345,0.014583413590548724,0.018204450536628173,0.024232991510951037,0.03079241552080987,0.037126541740713025,0.04290693831762704,0.04796472931605872,0.05220381743180425,0.055569461502276575,0.05803522327789565,0.059596842798127846,0.06026904378966532,0.06008368340568184,0.059088524473910796,0.05734623849698704,0.0549333751461989,0.051939082003197745,0.048463385209805164,0.044614892818000934,0.040507914747283394,0.036259285140028595,0.031985706497844435,0.027803193677945395,0.023830783890754503,0.020199800057450142,0.017064978241772204,0.014602522365309316,0.012972892492942822,0.012265241710561755,0.012516631174350423,0.013804582266222627,0.016231735635632488,0.01981016066358342,0.024430830711141178,0.0299206085618848],[0.1235607158777237,0.11754804166029499,0.11112472392003747,0.10428812671438321,0.09704057438255685,0.08939034136537972,0.08135278129203811,0.07295163840140056,0.06422063362798817,0.055205546067759764,0.04596737986859203,0.036588426949125986,0.027187947837327506,0.01798072452860338,0.00963920566030469,0.006426758155933287,0.012330994676087049,0.019984455764195913,0.02739926905671322,0.03420269483090969,0.040243853046470275,0.04543595026618166,0.04972453821558648,0.05307802660646239,0.05548399504375266,0.05694747503479452,0.05749004853615575,0.0571493274439829,0.05597859546003344,0.0540464527529691,0.051436300976271145,0.048245472723281425,0.044583760405896275,0.04057105457463811,0.03633380601471165,0.032000181149699714,0.027694280687801002,0.023530908005395017,0.019614191346221735,0.016044922196738948,0.012939306198670751,0.010449534502918283,0.008752671480288974,0.00798754913215017,0.008255713669298594,0.00971753620525263,0.012484551068346051,0.016476641217994432,0.021500454569150854,0.027348668657855544],[0.12371912972361669,0.1177289448318862,0.1113313754834477,0.1045243362424015,0.09731083909806792,0.0897000403660915,0.08170846256963533,0.07336146450170829,0.06469511494713885,0.05575883354629352,0.04661974267726634,0.03737152118772198,0.02815757444895762,0.019252491231641085,0.011472251086322511,0.008291768635069892,0.01286464129548623,0.01990095341568842,0.02697997711064536,0.033541323671034955,0.039376163381217626,0.0443749696778533,0.04847256313348857,0.05163161293560228,0.05383642655408008,0.055090231193996725,0.05541388624743272,0.05484527380663312,0.05343902956745874,0.051266410680386475,0.04841512295758451,0.04498889906573886,0.04110654432705037,0.03690004699390838,0.032511190921017855,0.028085961520810995,0.023766095713968944,0.019677924021234278,0.0159211881870602,0.01256541419637013,0.00966542993182446,0.00730043244560374,0.005614550767972551,0.004815914539554229,0.005179789468549429,0.006975073843936454,0.01017543113259197,0.014554338150297354,0.019885904552963365,0.02597591124498027],[0.12425768520262245,0.1183475156560728,0.11204287971509996,0.10534434915028967,0.09825840709304755,0.09079886503962069,0.08298868293232856,0.07486244543132509,0.06647000644748806,0.05788240907076198,0.04920265308147538,0.04058776111315184,0.032299474821411746,0.024830255911109076,0.019187911206102526,0.017050536286444356,0.01917039646206636,0.023941090969241085,0.029596215648235148,0.035219815528268014,0.04038043262206671,0.04485534561725629,0.04851942114105375,0.05130129977746589,0.05316471063456828,0.0540998146334811,0.05411895132924053,0.0532545123663605,0.05155792753629052,0.049099253575943316,0.04596705669571619,0.04226834044329668,0.0381282446514109,0.03368913041675139,0.02910843212892137,0.024554222223554075,0.020196718895208687,0.016193171644562788,0.012664232286441675,0.009666886138718625,0.007186540408164897,0.00518114259541093,0.003685482533242016,0.002982008028832194,0.0036714438420325877,0.0059333551040336155,0.009484636383931325,0.014091442179497315,0.019573816567156635,0.02576778562055267],[0.12515955382090188,0.11938275798905355,0.11323277949469086,0.10671442633447115,0.099839625109155,0.09262932508068304,0.08511605499644986,0.07734753102757959,0.06939204949638324,0.061347054334105276,0.053353542560586276,0.04562124044182117,0.03847214242396135,0.03240488073102192,0.028130855160869984,0.026380781923095356,0.0273361734811207,0.03034304905395624,0.034432338386522696,0.038830808923029585,0.043041917438387214,0.04676292830908057,0.049808949788101894,0.05206777450132661,0.053475400673907596,0.05400285317892428,0.05364899670882685,0.05243660500644537,0.05041027647228923,0.047635441009077524,0.04419802297313201,0.0402044765913532,0.035781968509348776,0.03107847128365139,0.026262426715633395,0.021521313651445627,0.017057504010721505,0.013077075250770731,0.009760780531022327,0.007200435141758394,0.005317882231866684,0.0038884728899128414,0.0027848012001391942,0.0024445439031515913,0.0036909304748420657,0.006349175383018195,0.010109787203678633,0.014823903757560188,0.020356075029253837,0.026564533223594092],[0.12639825455682183,0.12080176260560195,0.1148598139024225,0.10858229260419965,0.10198743935076073,0.09510413964914677,0.08797497936727014,0.08066045289679756,0.07324493252691124,0.06584531470723119,0.0586235261727477,0.0518036628197428,0.045691208292593356,0.040679981368982855,0.0372072760167878,0.035606512006331206,0.03589985341873342,0.0377313037474373,0.040535926190721994,0.04375949721456414,0.04696483352707161,0.049840110533781914,0.05217294352553135,0.05382342085407314,0.05470441769347342,0.054768761899400005,0.05400123478660441,0.052413719840592315,0.05004236931669257,0.046946076246851494,0.043205803535519643,0.03892448122659551,0.03422728411627594,0.029262184600523766,0.024200783899857994,0.01923961175581511,0.014602312993946273,0.010542335870901958,0.00733558336063693,0.005197861851334458,0.004012621752664845,0.0032472321007965704,0.0026105797032625797,0.0027929078822890373,0.004570535537521317,0.007586184757180327,0.011565434211637911,0.016393770332422435,0.02196606168792906,0.028164017313235912],[0.12793943985043185,0.12256217498306099,0.11687138908325106,0.1108821172454635,0.10461870573054802,0.09811724139703377,0.09142867536756395,0.08462287352390616,0.07779385395392915,0.071066372907667,0.06460352777517761,0.05861354897684074,0.053350436569933185,0.04909715092060539,0.04611613124422841,0.04456466891663208,0.04441235642052682,0.045425663352772754,0.04723921313485544,0.04945817341001856,0.05173044384504637,0.05377471164442891,0.05538070422645894,0.05639901264865439,0.05672972683641169,0.0563131146277426,0.05512285446628841,0.05316144776711148,0.05045728748861105,0.047062933267795426,0.04305425531115968,0.03853020975249206,0.03361310168217325,0.02844931660674125,0.023210755069954868,0.018097851345958437,0.013346786900271957,0.009247362473123277,0.0061739933251369825,0.004499923834750694,0.003992329602776862,0.003772086783922501,0.0035786772843339983,0.004169509048708341,0.006210486897191059,0.00946483267086653,0.013642073418726863,0.018594580370522175,0.024216585514954196,0.03040341348591778],[0.12974304926074057,0.124615108811392,0.11920756969461764,0.11354005498556474,0.10764198472522182,0.10155487685389986,0.09533513022235605,0.08905732467279256,0.08281795099608091,0.07673917290188013,0.07097154671511793,0.0656933685591191,0.061102511675766476,0.05739532589777933,0.05472950362570697,0.05317746861820451,0.05269068774646229,0.05309800176300563,0.05414179295763794,0.055531330138985625,0.05698814488598391,0.05827217744835067,0.05919105407163993,0.05959953594473694,0.05939495438112108,0.05851190955862743,0.05691764574380676,0.05460852452986313,0.05160759237101323,0.047963099815530645,0.04374781849781245,0.03905905121826878,0.03401933448143066,0.02877804510116999,0.023514597642535728,0.01844500351151707,0.013835596734127237,0.010026743624448007,0.007424885956821857,0.006233309456586993,0.005964702284672229,0.005902077336291415,0.005965080409166866,0.006751173058561215,0.00881421499658867,0.012107256111198093,0.01636262012675239,0.021380445947353114,0.027024906340494752,0.033185181353786335],[0.13176557454433593,0.1269081250713614,0.12180501973540066,0.1164794801723689,0.11096449757551595,0.10530479625503697,0.09955901575071247,0.09380198735871366,0.08812680173201984,0.08264604103729799,0.07749103461942604,0.07280733687950622,0.06874414869758451,0.06543594473686043,0.06297728588199311,0.06139681865200913,0.06064084572553555,0.06057540498938097,0.06100717170541253,0.061714161980113695,0.062474776799653506,0.06308826251446222,0.06338562072792199,0.06323338559864639,0.06253330521907227,0.061220243949307016,0.05925969354802406,0.05664558951240708,0.05339872353778635,0.0495658466550662,0.045219493691771556,0.04045858638120894,0.035409985874421186,0.030231391608529588,0.025116316280738633,0.020301868993103146,0.01607685635596396,0.012769088324106755,0.01063873145083344,0.009629440340911682,0.009297276559017726,0.009225791161211576,0.009429655180675718,0.010333181647285698,0.012359009150655577,0.015568173389770507,0.019771835595962614,0.024758297590934675,0.03036261176536889,0.03645671939887158],[0.13396221230977778,0.1293879656833301,0.12460046392779323,0.11962533520622676,0.11449749963594817,0.10926268303164913,0.10397890888682354,0.09871775718278213,0.09356501426590538,0.08862010307187491,0.08399340529491056,0.07980038605887897,0.07615157797970819,0.07313836935459274,0.07081639918347572,0.06919067216823968,0.06820769970045903,0.06775839206551623,0.06769130437390952,0.06783180021956954,0.06800139508123008,0.06803316321338419,0.06778178514523144,0.06712883604978813,0.06598475047057685,0.0642888879472954,0.062008766746248216,0.05913914849563834,0.05570136958695171,0.051743142526067966,0.047338971446355356,0.04259131415808001,0.03763264142500889,0.03262848428069606,0.027781021512747976,0.02333040141556088,0.019543442249844677,0.01666414122622149,0.0148013494691873,0.013819038315119107,0.013406339069250735,0.013334026220685984,0.013651899598114772,0.014658300893600453,0.016662096434588883,0.019758125437920267,0.02383430927945429,0.02870603581155664,0.034200895407409296,0.04017739530480147],[0.1362887423957004,0.13200283930071402,0.12753343015403987,0.12290734213382377,0.1181598863216891,0.11333589949178285,0.10849058679683163,0.10368993212518111,0.09901032570770821,0.09453692802668989,0.09036019409717508,0.08657002389392163,0.08324733218262295,0.08045356935041757,0.07821980730334833,0.07653799734401501,0.07535718542448196,0.07458633602585249,0.0741033143968915,0.07376764523750681,0.07343394372248635,0.07296353082341481,0.0722330203097678,0.07113982401519044,0.069605189382659,0.06757558259728813,0.06502315273541502,0.06194583447558854,0.05836747192164077,0.054338212295947645,0.04993532338233613,0.04526449865949653,0.040461539801788834,0.035693819492917875,0.031159586229600855,0.02708000356136258,0.023673541439970143,0.021101114141403123,0.01939314600242209,0.018421582600515102,0.017983090608514763,0.017953257242586992,0.018389397415526868,0.01950204615636442,0.02151234034386935,0.024511880335394327,0.028439353824462832,0.033149702419034345,0.038482920860113214,0.044295361024369304],[0.13870304081277934,0.13470416805268237,0.13054820594331762,0.12626208660574567,0.12188021988812346,0.11744510456309322,0.11300763443854436,0.10862688694681569,0.10436911465637709,0.10030561071902147,0.0965091297072303,0.09304867764760683,0.08998280084133406,0.08735201124287321,0.08517157197492704,0.0834262633346323,0.08206864146990354,0.08102155881565082,0.08018458099245304,0.07944293317495293,0.07867718890155338,0.07777215401401699,0.07662402939312175,0.07514559974490106,0.07326966343679842,0.0709511405548495,0.06816833261457411,0.06492374310961326,0.06124476736828232,0.0571844525650102,0.0528224090179523,0.04826577597577283,0.04364979692096622,0.039136820290467535,0.03491109353961089,0.031164542701859435,0.02806764964598688,0.025725602582076318,0.024139354320595875,0.023210290752507436,0.022808186115922616,0.02286611404984668,0.02343624859370643,0.0246664643041391,0.026712150441571957,0.0296476450369646,0.033438965965712886,0.03797640870679221,0.04312180096546872,0.04873960640017028],[0.14116619919525894,0.1374477935249861,0.13359506389476658,0.12963413754464476,0.12559753190554124,0.12152441024849375,0.11746048738955596,0.11345741374922716,0.10957143821606175,0.10586115090642742,0.10238416403288783,0.09919273307787392,0.09632856663629186,0.09381739429702717,0.09166416486511389,0.08984988497234118,0.08833094752529265,0.08704132217694953,0.08589733634190543,0.08480422072299099,0.08366333794126694,0.0823791032980653,0.08086493031548496,0.07904791790839844,0.07687230822544837,0.07430193076307481,0.07132191813019852,0.06793996700373862,0.06418735699944034,0.06011984484265594,0.05581840926043593,0.05138958593693082,0.04696470926947292,0.042696647519761884,0.03875157305775434,0.035292537158777046,0.032453144921739896,0.030306623719072223,0.02884723225687946,0.028004946104173763,0.027696247627498612,0.027884222909425018,0.028609992168202678,0.029974900317636843,0.03208475512151094,0.03499309742031379,0.03867792877350606,0.04305572241174541,0.04801127454099436,0.05342301618939009],[0.1436432695059032,0.14019469862100106,0.13663087686735903,0.13297642551283403,0.1292612758262862,0.1255206543193851,0.12179471719312034,0.11812770714031506,0.1145665034088118,0.11115846178089576,0.1079485103428945,0.10497559072066429,0.10226870871088604,0.09984305161327861,0.09769677979491397,0.09580912986131417,0.09414032220918449,0.09263345799786807,0.09121820926434454,0.08981578207049282,0.08834447120704539,0.08672515421210684,0.08488624285872677,0.08276783558003756,0.08032501810874092,0.07753039997267289,0.07437604291383237,0.0708749438943937,0.06706219259695154,0.0629958339134815,0.058757314590465064,0.054451142365750466,0.05020298365614475,0.04615485872155808,0.042455554091696115,0.03924458785233186,0.03663047145884952,0.034669611987557795,0.033358217575080444,0.032648106675852745,0.032483765641296326,0.0328416594745287,0.03374893222857141,0.03527075556792171,0.03747470571243787,0.04039408518732528,0.04401002857786532,0.04825655815940238,0.053038525820490644,0.058250155770152724],[0.14610368136964477,0.14291133098608552,0.13961926507618055,0.13625009990708184,0.13283074794020672,0.12939221297135242,0.1259690608516134,0.12259847930189484,0.11931885220797693,0.11616780851413162,0.11317977041236564,0.11038312129861198,0.10779723095314318,0.10542968824779386,0.10327416191568801,0.10130929810120246,0.09949894905838648,0.09779382631069371,0.09613443711022963,0.09445496540393543,0.0926876531412997,0.09076724184938215,0.0886351254743623,0.08624299889609205,0.08355591782283553,0.08055478515066347,0.07723833367558704,0.07362468397944995,0.06975252071202977,0.06568184640631605,0.06149412496207734,0.0572913932230371,0.053193584243326535,0.04933292726282712,0.04584413265298902,0.042849768062234034,0.04044262387379789,0.038670877903417715,0.03753474831039717,0.037000372599980694,0.03702695180850202,0.03759367454888225,0.03871202169181385,0.040417628817784705,0.042747665016364296,0.045717049615624415,0.04930530513564886,0.053457456533399485,0.05809435449216565,0.06312536619002396],[0.14852139240453055,0.14556962075275476,0.14253041023287139,0.13942405097245816,0.1362742154266983,0.13310763141274876,0.12995347103104823,0.12684240146348547,0.12380526166474076,0.12087136379240222,0.1180664719455408,0.11541058067637044,0.11291569173710082,0.1105838515719518,0.1084057413712625,0.10636008636097721,0.1044140648580624,0.10252476405691018,0.1006415805738898,0.09870933863031378,0.09667182798491475,0.09447545799908205,0.09207277299385132,0.08942565342130249,0.08650811104039992,0.08330865377133632,0.07983223514579585,0.07610180850955647,0.07215947333115573,0.06806712315179793,0.06390636965365351,0.05977731231317482,0.05579545750254577,0.05208585405243457,0.048773571194802474,0.045970497337886454,0.043760542368373054,0.04218820901947579,0.041256866621107,0.04094002087739659,0.041201777275424296,0.04201667398443358,0.0433792328396244,0.045299738396847714,0.04779030146150625,0.05084949976738189,0.05445288134772296,0.05855197244115851,0.0630798224141953,0.06795918222641088],[0.15087483362940426,0.1481467788308776,0.1453406508850675,0.14247423904245252,0.13956791527799775,0.13664423856294378,0.13372732005372323,0.1308419194129943,0.12801226182413916,0.12526059609293888,0.12260555618523136,0.12006043776435325,0.11763154952405287,0.1153168342945502,0.11310496385856525,0.11097508455171104,0.10889732702200677,0.10683410321583518,0.10474211633492436,0.1025749277577297,0.1002858762630823,0.09783113601774447,0.09517272560947611,0.09228132767362208,0.08913883149308126,0.08574055539171188,0.08209713168036968,0.07823603733256981,0.07420272207133648,0.07006121369090523,0.0658939571194405,0.061800461524746275,0.05789410775975739,0.05429630403626044,0.05112732057750855,0.04849399313490134,0.04647634248383071,0.04511744233207913,0.044421651030486446,0.04436356095612269,0.044904425602645334,0.04600847274721399,0.0476519453229395,0.0498223110589934,0.052510273724157966,0.055699931144303376,0.05936184825085633,0.06345115708803112,0.06791006003053505,0.07267268427938854],[0.1531467068437756,0.1506249487531915,0.148031947986358,0.1453829323703009,0.14269502834979267,0.13998683581004462,0.13727780788373536,0.1345874229786201,0.13193415436257988,0.12933426813844168,0.12680051195735392,0.12434079065836229,0.12195695503527576,0.11964384833656477,0.11738875441821159,0.11517136721229085,0.11296435432113365,0.11073452543739265,0.10844455112555543,0.10605512271194495,0.10352740998603353,0.10082566435572188,0.097919828504245,0.09478804188259626,0.09141896471622606,0.08781387204630102,0.0839884855440558,0.07997450736198151,0.07582078949734562,0.07159400398937127,0.06737856115967507,0.06327534638267575,0.05939862855832187,0.05587033132929362,0.05281099590395735,0.05032759705453777,0.048500159496021315,0.04737129129552225,0.046943479111708084,0.047186445854233164,0.0480518324687419,0.04948864797864672,0.05145331334663317,0.053911903011249276,0.05683624591261601,0.060197598286520396,0.06396133273755479,0.06808447254876622,0.07251616157375428,0.07720009118411017],[0.15532368231707103,0.15299076993090824,0.15059128600712252,0.1481379213455523,0.14564468997429286,0.14312650182627606,0.14059858041736567,0.1380757240797897,0.13557142503673436,0.13309688082162896,0.13065995562656735,0.12826417203430804,0.1259078318895359,0.12358337388771559,0.12127707062489991,0.11896914743565548,0.11663437086544212,0.11424311125077528,0.11176283936845634,0.10915997968509616,0.10640201871375171,0.10345975910732216,0.10030961712915115,0.09693587858443783,0.09333284996559034,0.0895068608185555,0.08547808365589689,0.08128213221911965,0.07697136867613308,0.07261578254412032,0.06830318101946407,0.06413823504726304,0.06023966562510678,0.05673462228195438,0.05374936894523156,0.05139622410792774,0.049758670234991795,0.04887908707052015,0.04875459751010185,0.04934388144440267,0.05058235941409178,0.052399038856986,0.054728684164358665,0.057516700361736,0.06071791240913551,0.06429225005217874,0.0682002180847656,0.07239988800435891,0.07684589377070596,0.08149005968402591],[0.15739603560905235,0.15523489582018576,0.1530100550186052,0.1507317516757307,0.14841106980390348,0.14605952722342233,0.14368854344593718,0.14130879280659833,0.13892946154697206,0.13655744314944945,0.1341965228346077,0.13184661737777997,0.12950314728504556,0.12715662184411952,0.12479251134830392,0.12239146421204702,0.11992990125694206,0.11738098878574563,0.11471596121739273,0.11190573821305448,0.10892276437304182,0.10574299357047164,0.1023479442319104,0.09872676375695803,0.09487825584630814,0.0908128391291783,0.08655441383091307,0.08214210842233692,0.07763184967322732,0.0730976297193012,0.06863220504534917,0.0643467202961278,0.06036838932690008,0.05683496993007875,0.05388466716154744,0.05164097121533944,0.05019444092697431,0.04958699377537963,0.049805966943432395,0.05079188911306867,0.05245675680956014,0.054704502136921386,0.05744615532447203,0.06060685283049525,0.06412602687953861,0.0679538416094212,0.07204669391977678,0.07636353330090391,0.08086368141935434,0.08550609129644901],[0.1593572533081034,0.15735149823390893,0.1552834437289222,0.15316100128168386,0.1509925352743487,0.1487864773589673,0.14655084937224064,0.1442927044928873,0.1420175068854585,0.1397284818861068,0.1374259805902804,0.13510691273655745,0.13276430802876274,0.13038706663543226,0.12795995334710722,0.1254638766836526,0.12287647543368815,0.12017301325810002,0.11732756046125725,0.11431442421462877,0.11110977704572045,0.10769342962089754,0.10405069762415656,0.10017432244578017,0.09606641907719314,0.09174043893582683,0.08722314606997875,0.08255660550859076,0.07780015982371247,0.07303230014103708,0.06835217752325728,0.06388018406894488,0.05975649720946373,0.05613577640287703,0.053175756499278845,0.051018388042903866,0.04976575417792483,0.0494586383706458,0.05006855902202892,0.051508872026158496,0.05365961402629083,0.056394042460093004,0.059597337794869504,0.06317486724131831,0.06705241650404639,0.07117219485665387,0.0754876782994042,0.07995907473067294,0.0845501308730443,0.08922632735018529],[0.1612036296310856,0.1593377792291033,0.15740986206797397,0.15542561364593527,0.15339090208321035,0.15131137393145708,0.1491920320533066,0.14703675729666005,0.14484779401532952,0.14262522831359845,0.14036649619915403,0.13806596534491117,0.13571463754946486,0.13330001812666664,0.13080619275326177,0.12821414195174188,0.12550230946727733,0.12264742517627121,0.11962556815722589,0.11641344347743485,0.11298983896450124,0.10933722684299291,0.10544347987810952,0.10130368209369217,0.09692202916663406,0.09231383160702977,0.08750765197343333,0.08254761963209852,0.07749595909990285,0.07243570962320588,0.06747343943722477,0.06274135048065968,0.0583973679127847,0.05462055581958153,0.05159801634050903,0.04950017009332563,0.048446821823447575,0.048476316405158766,0.04953544209902052,0.051498025289835186,0.05420152371369852,0.05748241964011213,0.06119834577992348,0.06523603574173173,0.06950992538312219,0.07395654321814649,0.07852808433743479,0.08318686118901694,0.0879012183526216,0.0926429046325944],[0.16293386941751936,0.16119350454011983,0.15939040389680742,0.15752829263381807,0.15561076891082384,0.15364098290474526,0.15162126661676628,0.14955272688044643,0.14743482045136092,0.14526493658849476,0.14303801833285512,0.14074625784963896,0.13837890285355164,0.13592220962392643,0.13335957318512645,0.1306718571742273,0.1278379356245352,0.12483544773677205,0.1216417563505887,0.11823509294031465,0.11459586797363393,0.1107081264316844,0.10656113483698648,0.1021510986420041,0.09748302756315429,0.09257279157632332,0.08744944131811024,0.0821579002482657,0.076762160157939,0.07134909179682243,0.0660328312068402,0.060959227699899296,0.056308697789461376,0.05229365668160666,0.049143916867442,0.04707318085793389,0.04622846099153778,0.04664316879485012,0.048225216750894896,0.05079105570124689,0.05412220241118296,0.0580122798975795,0.06229095127333203,0.06682879484368044,0.0715321733160809,0.07633485567678532,0.08118985807256517,0.08606282226816352,0.0909271871470282,0.09576096466088954],[0.16454870804044908,0.1629205670746712,0.16122835499128177,0.1594739591057284,0.15765893051866453,0.15578419577168523,0.1538497339398444,0.15185423138517526,0.14979473138658977,0.147666300653467,0.14546173873685111,0.14317135894586672,0.1407828699949052,0.1382813858767535,0.1356495873133562,0.13286805189969642,0.12991576244281042,0.1267707950499716,0.12341118147695133,0.11981593539025978,0.11596623072504567,0.11184672330825539,0.10744701539795465,0.10276327796925672,0.09780006914699749,0.09257242162713468,0.08710832046743648,0.08145175785496324,0.07566662988691782,0.06984180570677741,0.06409765699092682,0.058593916377839506,0.053537302647272675,0.04918382219853948,0.04582456398772838,0.04373981727852455,0.04311951822682316,0.043987132710491754,0.04618774873756477,0.04945384321695611,0.053494771128115445,0.058056725765723446,0.06294369984614576,0.06801479820596949,0.07317294044999574,0.0783527888520928,0.0835106802838162,0.08861706168774366,0.09365115014441863,0.09859735865837246],[0.16605055498120852,0.164522585146858,0.16292874793936538,0.16126926698582955,0.15954386216432428,0.15775149200318364,0.15589007275417124,0.1539561856898508,0.15194478798469047,0.14984894602977064,0.1476596127701827,0.14536547220939067,0.14295287423874717,0.1404058812246023,0.13770644435269816,0.13483472289595663,0.1317695539160717,0.12848907423675576,0.12497149179171331,0.12119600067830998,0.11714383449227368,0.11279945690307767,0.10815189831497442,0.10319626478627208,0.0979354732425858,0.0923823105164126,0.08656198107721005,0.08051541164862563,0.0743037347630575,0.06801458229672201,0.06177102935128734,0.05574396129849038,0.050167348821578396,0.04535097755231568,0.0416729639590287,0.039518872403986764,0.03914975164955195,0.04056833961185487,0.043513827793466346,0.04759482141074796,0.05243119808909798,0.05772195963951123,0.06325255654491163,0.06887833619288215,0.07450490269968396,0.0800720729367933,0.08554220326431015,0.09089207217634027,0.09610737233861005,0.10117906354737047],[0.16744316506122478,0.16600453751140018,0.16449796344293455,0.16292217514355223,0.16127526819482477,0.15955447201666348,0.15775590558046404,0.15587432890258424,0.15390290381558425,0.1518329800372842,0.1496539244019448,0.14735301198758735,0.144915397545633,0.14232418401861163,0.13956060209603846,0.13660431098049347,0.1334338262793545,0.13002707682755651,0.12636208902638235,0.12241779578075437,0.11817496825454621,0.11361727354764417,0.1087324715555921,0.10351378210655705,0.09796148310466143,0.09208484918895166,0.08590462155839954,0.0794563366889904,0.07279507527702159,0.06600258589857133,0.059198357334295175,0.05255698298834219,0.04633419474290505,0.040899284197635055,0.036750967905647684,0.034447371844885236,0.034376005901368495,0.03649363573296222,0.0403514647084533,0.045376710025523743,0.051088308592429826,0.05714911227099124,0.06334032391798744,0.06952456516283262,0.07561736835753563,0.08156811376158278,0.08734769258846438,0.09294050210972972,0.09833920813227871,0.10354131792013709],[0.16873133937518586,0.167372435562447,0.1659433763019474,0.16444157098204204,0.16286368821778477,0.16120545172203565,0.1594614276791973,0.15762481318733718,0.1556872375069135,0.15363858966236782,0.15146688715810436,0.14915820099136567,0.14669665163433018,0.1440644891800141,0.1412422684923375,0.13820912720045916,0.1349431710953295,0.13142196840022385,0.12762315206432448,0.12352512831613753,0.11910789096773441,0.11435394535484426,0.10924935477046623,0.10378493820585595,0.09795767550306346,0.09177242287897602,0.08524412423117787,0.07840085362078703,0.07128830664792922,0.06397690521931534,0.05657375222436877,0.049243710034056,0.04224713612533829,0.03600318184878881,0.03116538301700575,0.028584892383266818,0.02889700105370492,0.03194663885279821,0.03693269227514354,0.04303098332316812,0.04967238225912771,0.056513536973696654,0.06335369547823637,0.0700758762476832,0.07661264429086773,0.08292661437623236,0.08899897662166331,0.09482243416367053,0.10039668945224621,0.10572549822124074],[0.16992065663200873,0.16863303200597132,0.16727304376278027,0.1658369416673891,0.16432015507868825,0.1627171114187495,0.16102105081930107,0.15922384546151533,0.1573158337530963,0.15528568077202426,0.15312027718439217,0.15080468897788596,0.14832216976001067,0.1456542460457506,0.1427808839905698,0.13968074359701935,0.13633152381341967,0.13271039950360924,0.12879454940948531,0.12456177341969865,0.11999119824660813,0.11506407371733166,0.10976466839376196,0.10408128503564726,0.098007437058023,0.09154326365213425,0.08469732820612697,0.07748907347475482,0.0699524683747498,0.06214194274124864,0.05414298299154988,0.04609281566690286,0.038224072278798975,0.030960878819623755,0.02511061083150347,0.022026092466523553,0.022894753957053912,0.027252294716380545,0.03361324783366706,0.040870225010682125,0.04843783761092512,0.05601887207417842,0.06345656304021233,0.070665754387512,0.07760075232642231,0.0842391149086521,0.09057268550547712,0.09660219551211784,0.10233380177829192,0.10777678126439173],[0.17101723471911334,0.16979356470199844,0.16849543370091144,0.16711808923770302,0.16565589978429568,0.1641021933805176,0.16244909586630607,0.16068737625741483,0.15880630801206772,0.15679355584541746,0.1546350982307119,0.15231519568838744,0.14981641435823126,0.1471197131848753,0.14420460139959124,0.14104937099525539,0.1376314067694139,0.13392757450082957,0.1299146862058643,0.1255700404918005,0.12087203611448734,0.11580085836344975,0.11033924143488817,0.10447331654619074,0.09819356719783419,0.09149593384083089,0.08438314925094667,0.07686646367660206,0.06896808508956821,0.06072504432066246,0.052196165969470056,0.043476542693999545,0.034732458323997774,0.02630002214920551,0.019000681637091666,0.014950995831641405,0.01677582897185931,0.023009027622641308,0.030912571478831155,0.039283941739000156,0.04767249909931334,0.055882771185035394,0.06381846759449603,0.0714298176960015,0.07869248528855784,0.08559753944189757,0.09214589059010428,0.09834480554828012,0.10420554187221998,0.10974167502505405],[0.17202752172931257,0.1708615340466779,0.16961919011489912,0.16829488624230668,0.16688209937531637,0.16537324379138368,0.16375952995273327,0.16203083216643877,0.16017557261330895,0.15818062995516205,0.15603128102288968,0.15371118396461242,0.1512024106673059,0.14848553527325303,0.14553978425893907,0.14234325193849148,0.13887318354360018,0.13510632638799344,0.13101934822616612,0.12658932093666192,0.12179426726062291,0.11661376866159721,0.11102963362394204,0.10502662816109291,0.09859327453021512,0.09172273139757953,0.0844137818584577,0.07667198175645881,0.06851107749968978,0.05995493941412929,0.05104062545879895,0.041824326385760176,0.03239611385357659,0.022928964168197393,0.013918655245588293,0.007969002471488884,0.011734652504022858,0.02026591658401529,0.029491911583994224,0.03869205783863252,0.047661995399938324,0.05631281498558021,0.06459832797359566,0.07249450119096083,0.07999125156903536,0.08708811156049115,0.09379142001961382,0.10011226826071792,0.10606491362210187,0.11166553804938495],[0.17295811532540797,0.17184451211045748,0.17065293351802885,0.16937706897369192,0.1680096644854127,0.16654239574340382,0.1649657453136837,0.16326888981292376,0.16143960365453186,0.1594641864299551,0.15732742117575843,0.1550125706367738,0.1525014181568651,0.14977435903315423,0.14681054711334743,0.14358810018767143,0.14008436644037395,0.13627625300846558,0.13214061667690896,0.12765471603960118,0.12279672417677912,0.11754630112754749,0.11188522625444046,0.10579809212702947,0.09927306404829185,0.09230271341582506,0.08488494022962728,0.07702401393749705,0.06873179218714284,0.060029251485048,0.05094866888039233,0.04153744406747263,0.03186703770521421,0.022063022865261957,0.012471533329755508,0.005682765510138155,0.010950923907840244,0.02031456344322705,0.02995639858042075,0.039440480721251295,0.04863520408601588,0.057475899949137536,0.06592584741135843,0.07396494295149476,0.08158470845133592,0.08878529126717878,0.09557328653382123,0.10196000790432676,0.10796007180432451,0.11359023900361395],[0.17381560908842317,0.17274998168651529,0.17160509394882809,0.17037406570352193,0.16904906388458196,0.1676211907558318,0.16608037776210235,0.16441529027109097,0.16261324902698077,0.16066017450813744,0.15854056052674886,0.15623748330595613,0.1537326519205497,0.15100650541803706,0.14803836120298794,0.14480661845042214,0.14128901951733064,0.13746297166643964,0.1333059310386034,0.12879585086213904,0.1239116965531962,0.11863403189661312,0.1129456833178457,0.10683249413143596,0.1002841891161519,0.09329538506676974,0.08586681230647626,0.07800687236952039,0.06973379033335514,0.061078940878839465,0.052092777522940864,0.04285733593419113,0.03351810532970025,0.02438490127913359,0.016333253712029587,0.012266212950827814,0.015765215195397798,0.02356679083515667,0.03252506003036766,0.04168150694383874,0.050711200531835185,0.05947061723181113,0.06788529241685347,0.07591456250837993,0.08353759573854051,0.09074658040158684,0.09754276051261207,0.10393379682317698,0.10993184997816682,0.11555212142578228],[0.1746064643462097,0.17358520337880495,0.17248377443403531,0.17129485758388777,0.1700101836765399,0.16862043673433588,0.16711516327001755,0.1654826932923939,0.16371007824046435,0.16178305140813748,0.1596860165766065,0.15740207055021127,0.1549130651063579,0.15219971355622214,0.1492417467312986,0.14601812284848906,0.14250729547810342,0.1386875438912637,0.13453737058486753,0.1300359720313437,0.12516379105878603,0.11990316335288613,0.1142390774659427,0.1081600794243377,0.10165937344145648,0.09473620727585334,0.08739770118736392,0.07966142052950569,0.07155929139084947,0.06314413512313902,0.05450173386872484,0.04577558358641029,0.037223108328617985,0.029352720155327874,0.02323280910357437,0.02074473669337722,0.023152771566713047,0.02918045368179954,0.03693189638693348,0.045333174447798455,0.05387779897438671,0.06231419010106154,0.07050680093486983,0.07837891081772277,0.08588717998803908,0.09300902297281927,0.09973559959159341,0.10606750585047729,0.11201189385423055,0.11758042672464208],[0.17533690587284476,0.17435710883816977,0.17329664280242024,0.17214787001405443,0.17090221900689656,0.1695501004814317,0.16808083126015216,0.16648257071692873,0.16474227450077505,0.16284567069017714,0.16077726371498025,0.1585203714729723,0.15605720107079482,0.1533689685789967,0.15043606818013694,0.1472382962082625,0.14375513596669046,0.13996611005863752,0.1358512085392894,0.13139140389440712,0.12656926829125037,0.12136971576382241,0.1157809037792721,0.10979534822685112,0.10341133933588818,0.09663480506465445,0.08948187641187431,0.08198261374455991,0.0741867555611095,0.0661731672154609,0.05806635015998948,0.05006675028750616,0.04250726991999842,0.0359500834950576,0.03128912950265998,0.029604253845548493,0.03141917309100279,0.03614115911316155,0.04267747116250101,0.0501499657169228,0.0580136510074755,0.06594931057906331,0.07376791870454646,0.08135528085768781,0.08864218672019977,0.09558794447463727,0.10217078624450047,0.10838191188443959,0.11422156120804719,0.1196962888474882],[0.17601283976315998,0.17507221822088292,0.17405084975720728,0.17294089230621237,0.17173359616331252,0.17041923283690316,0.16898703305871016,0.16742513808592552,0.1657205688317282,0.16385921769712852,0.16182586824663495,0.15960424808769194,0.15717712051206315,0.15452642069166891,0.15163344257476769,0.14847908321870537,0.145044152287791,0.14130975607253984,0.13725776798915715,0.1328714016092952,0.1281359086585435,0.1230394344290422,0.11757407890338151,0.11173723743107676,0.10553333682063569,0.09897615335695858,0.0920920204310395,0.08492444436949413,0.07754101487672946,0.07004412130351263,0.06258794488174492,0.055405183843034674,0.04884575237151286,0.043417485817736814,0.03977624434706463,0.0385520308982427,0.03999707521713277,0.04379402447871105,0.04928836073077789,0.055832284218899034,0.06293579322275371,0.07026588534654946,0.07760396767739829,0.08480774776575264,0.09178521033209489,0.09847800712697724,0.10485086287924146,0.1108846424743718,0.11657165370006567,0.12191235243438686],[0.1766397917094568,0.1757365798918252,0.17475297107361526,0.17368102342908864,0.17251192284435665,0.17123592432250892,0.1698423035899009,0.1683193228530426,0.16665421506194922,0.16483319140842034,0.16284147713536032,0.16066338107871556,0.15828240474747932,0.155681397232646,0.1528427629148137,0.14974872994207356,0.14638168895715584,0.14272461382469415,0.1387615795229564,0.13447839748329685,0.1298633963510515,0.12490838776462514,0.11960987447845879,0.11397058548941352,0.10800146538229528,0.10172431172227446,0.09517535810744117,0.0884102581363448,0.08151114814666958,0.07459672022348704,0.06783630896223014,0.06146811385847437,0.05581770647642627,0.05130195089955229,0.04838509420820985,0.0474529575626112,0.04864212267080608,0.05176413782184118,0.05640580333963202,0.062101208685797195,0.0684451461035192,0.07512704512208863,0.08192288367240687,0.08867574951587069,0.0952777454978033,0.10165617947381524,0.10776367212537961,0.11357116484120117,0.11906293682251261,0.12423299497994728],[0.17722286383579872,0.17635573032817495,0.17540897170975836,0.17437464149178145,0.17324396418212368,0.1720072888491522,0.17065405388875793,0.16917276682034077,0.1675510033569084,0.16577543040798912,0.1638318580965449,0.1617053263305652,0.15938023201154167,0.1568405036521889,0.1540698311090521,0.1510519594434675,0.147771057789117,0.1442121767814436,0.14036181195613576,0.13620859607412894,0.13174415134399073,0.12696414411220142,0.1218696014141027,0.11646857314015296,0.11077825853255359,0.10482776465704836,0.0986617290456658,0.09234511221874511,0.08596951481236223,0.0796612918246878,0.07359124177851897,0.06798412318806869,0.06312270906814184,0.05933518819315512,0.05695057944946181,0.056217495215009274,0.057216787061584375,0.05982780967803363,0.06377662279400911,0.06872687956518894,0.07435557270240836,0.0803907720831869,0.0866198953724221,0.09288376725051184,0.09906653272902738,0.1050859022891067,0.11088509688458707,0.11642658410786753,0.12168730795972084,0.12665506770037946],[0.1777667081816281,0.17693467210833475,0.17602418952247031,0.17502739448223012,0.17393564186967056,0.17273947267946527,0.17142859145515268,0.16999185961140006,0.16841730881495245,0.16669217904659905,0.16480298644980196,0.16273562661870708,0.160475519634402,0.15800780398796324,0.1553175876208637,0.15239026578804363,0.14921191746860502,0.1457697948323727,0.14205292411298126,0.13805284153810873,0.13376449525493372,0.12918735414342492,0.12432677783083201,0.11919571985181482,0.11381685787778181,0.10822526933793877,0.10247179005450438,0.09662718669834199,0.09078719016579738,0.08507816701040502,0.07966254614453348,0.0747417806761846,0.07055248016536168,0.06734924201126435,0.0653687566797243,0.06477863704841301,0.06563013249971394,0.06784157955457383,0.07122365212776087,0.07553007017812254,0.08050679107747565,0.08592385851204255,0.09158913653063033,0.09735011348531548,0.10308994997974401,0.10872165859877914,0.1141823040714343,0.11942793640763966,0.12442941018606084,0.12916902252050072],[0.17827551487647864,0.17747786780694286,0.1766033361849363,0.17564420962613314,0.1745920535115844,0.1734376854835803,0.17217116494688656,0.17078179924126263,0.1692581705951279,0.1675881884438912,0.16575917221854747,0.16375797030952882,0.16157112162873566,0.15918506708561025,0.15658641943581236,0.15376230145055508,0.15070076431475557,0.14739130074803886,0.14382547074353433,0.1399976622540971,0.13590601484843934,0.1315535414700636,0.1269494918797354,0.12211101043174671,0.11706514832559696,0.11185129097641787,0.1065240427194669,0.1011565494087721,0.0958440892657613,0.09070744918418847,0.08589503270425064,0.0815817714112974,0.0779619454326992,0.07523279012265122,0.07356784471447989,0.07308451266575129,0.07381705809021888,0.07570781530786758,0.07862136476619988,0.08237426905353869,0.08676710361996533,0.09160893335730282,0.09673132756967241,0.10199375056737565,0.10728355519245526,0.1125132885814823,0.11761702821543886,0.12254665568157745,0.12726846979670484,0.13176027092361783],[0.1787530130181246,0.17798924757266185,0.1771505128297779,0.17622931861090918,0.17521750912289283,0.17410625003159702,0.1728860292793323,0.1715466752352788,0.1700773962122947,0.16846684586412417,0.16670321951113148,0.16477438705480207,0.1626680688647786,0.16037206190049777,0.15787452441659422,0.15516432896179813,0.15223149508851802,0.1490677153212683,0.14566699055255594,0.14202639416994847,0.13814698778917311,0.13403491516676375,0.12970270390933955,0.12517080527055385,0.12046939716131366,0.1156404578726062,0.11074007600351604,0.10584087578854899,0.10103427687501888,0.09643203904102282,0.09216614897805264,0.0883856513452719,0.08524876043777184,0.0829090340608121,0.08149616443451922,0.0810950333497203,0.08172953539706099,0.0833575926976941,0.08587957559829441,0.08915652356057402,0.09303130625597153,0.09734675927549977,0.10195799113013995,0.10673890079072162,0.11158434818211657,0.11640962788485955,0.12114854572293486,0.12575094378822727,0.13018015454326956,0.13441062417117708]],[],[]]},{"xaxis.title":"C","xaxis2.title":"C","xaxis.range":[-9.0,6.0],"xaxis2.range":[-9.0,6.0],"xaxis.type":"log","xaxis2.type":"log"}],"label":"C","method":"update"},{"args":[{"x":[[1e-06,1.757510624854793e-06,3.0888435964774785e-06,5.428675439323859e-06,9.540954763499944e-06,1.67683293681101e-05,2.94705170255181e-05,5.1794746792312125e-05,9.102981779915228e-05,0.00015998587196060574,0.0002811768697974231,0.0004941713361323833,0.000868511373751352,0.0015264179671752333,0.0026826957952797246,0.004714866363457394,0.008286427728546842,0.014563484775012445,0.025595479226995333,0.04498432668969444,0.07906043210907701,0.1389495494373136,0.244205309454865,0.42919342601287785,0.7543120063354607,1.325711365590108,2.329951810515372,4.094915062380427,7.196856730011514,12.648552168552959,22.229964825261955,39.06939937054613,68.66488450042998,120.67926406393264,212.09508879201925,372.7593720314938,655.1285568595496,1151.3953993264481,2023.5896477251556,3556.4803062231213,6250.551925273976,10985.411419875572,19306.977288832455,33932.217718953296,59636.23316594637,104811.3134154683,184206.99693267164,323745.754281764,568986.6029018281,1000000.0],[1e-06,1.757510624854793e-06,3.0888435964774785e-06,5.428675439323859e-06,9.540954763499944e-06,1.67683293681101e-05,2.94705170255181e-05,5.1794746792312125e-05,9.102981779915228e-05,0.00015998587196060574,0.0002811768697974231,0.0004941713361323833,0.000868511373751352,0.0015264179671752333,0.0026826957952797246,0.004714866363457394,0.008286427728546842,0.014563484775012445,0.025595479226995333,0.04498432668969444,0.07906043210907701,0.1389495494373136,0.244205309454865,0.42919342601287785,0.7543120063354607,1.325711365590108,2.329951810515372,4.094915062380427,7.196856730011514,12.648552168552959,22.229964825261955,39.06939937054613,68.66488450042998,120.67926406393264,212.09508879201925,372.7593720314938,655.1285568595496,1151.3953993264481,2023.5896477251556,3556.4803062231213,6250.551925273976,10985.411419875572,19306.977288832455,33932.217718953296,59636.23316594637,104811.3134154683,184206.99693267164,323745.754281764,568986.6029018281,1000000.0],[0.0006015170467586964,5357.645905431237,0.008579956814279222,0.002622938701902548,0.0034474437049411173,0.006440480639129858,0.0071292854503499405,0.0012445306696626736,0.0013349353055128505],[0.0006015170467586964,5357.645905431237,0.008579956814279222,0.002622938701902548,0.0034474437049411173,0.006440480639129858,0.0071292854503499405,0.0012445306696626736,0.0013349353055128505],[1e-06,1.757510624854793e-06,3.0888435964774785e-06,5.428675439323859e-06,9.540954763499944e-06,1.67683293681101e-05,2.94705170255181e-05,5.1794746792312125e-05,9.102981779915228e-05,0.00015998587196060574,0.0002811768697974231,0.0004941713361323833,0.000868511373751352,0.0015264179671752333,0.0026826957952797246,0.004714866363457394,0.008286427728546842,0.014563484775012445,0.025595479226995333,0.04498432668969444,0.07906043210907701,0.1389495494373136,0.244205309454865,0.42919342601287785,0.7543120063354607,1.325711365590108,2.329951810515372,4.094915062380427,7.196856730011514,12.648552168552959,22.229964825261955,39.06939937054613,68.66488450042998,120.67926406393264,212.09508879201925,372.7593720314938,655.1285568595496,1151.3953993264481,2023.5896477251556,3556.4803062231213,6250.551925273976,10985.411419875572,19306.977288832455,33932.217718953296,59636.23316594637,104811.3134154683,184206.99693267164,323745.754281764,568986.6029018281,1000000.0],[1e-06,1.757510624854793e-06,3.0888435964774785e-06,5.428675439323859e-06,9.540954763499944e-06,1.67683293681101e-05,2.94705170255181e-05,5.1794746792312125e-05,9.102981779915228e-05,0.00015998587196060574,0.0002811768697974231,0.0004941713361323833,0.000868511373751352,0.0015264179671752333,0.0026826957952797246,0.004714866363457394,0.008286427728546842,0.014563484775012445,0.025595479226995333,0.04498432668969444,0.07906043210907701,0.1389495494373136,0.244205309454865,0.42919342601287785,0.7543120063354607,1.325711365590108,2.329951810515372,4.094915062380427,7.196856730011514,12.648552168552959,22.229964825261955,39.06939937054613,68.66488450042998,120.67926406393264,212.09508879201925,372.7593720314938,655.1285568595496,1151.3953993264481,2023.5896477251556,3556.4803062231213,6250.551925273976,10985.411419875572,19306.977288832455,33932.217718953296,59636.23316594637,104811.3134154683,184206.99693267164,323745.754281764,568986.6029018281,1000000.0],[0.0006015170467586964,5357.645905431237,0.008579956814279222,0.002622938701902548,0.0034474437049411173,0.006440480639129858,0.0071292854503499405,0.0012445306696626736,0.0013349353055128505],[0.0006015170467586964,5357.645905431237,0.008579956814279222,0.002622938701902548,0.0034474437049411173,0.006440480639129858,0.0071292854503499405,0.0012445306696626736,0.0013349353055128505]],"y":[[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],[3.428714353076635e-05,55.38136172368294,690.33938400923,9319.742944380141,9422.61363120716,12399.99246609989,11469.710556154172,7436.440673474601,40394.43106054603],[3.428714353076635e-05,55.38136172368294,690.33938400923,9319.742944380141,9422.61363120716,12399.99246609989,11469.710556154172,7436.440673474601,40394.43106054603],[1e-06,1.757510624854793e-06,3.0888435964774785e-06,5.428675439323859e-06,9.540954763499944e-06,1.67683293681101e-05,2.94705170255181e-05,5.1794746792312125e-05,9.102981779915228e-05,0.00015998587196060574,0.0002811768697974231,0.0004941713361323833,0.000868511373751352,0.0015264179671752333,0.0026826957952797246,0.004714866363457394,0.008286427728546842,0.014563484775012445,0.025595479226995333,0.04498432668969444,0.07906043210907701,0.1389495494373136,0.244205309454865,0.42919342601287785,0.7543120063354607,1.325711365590108,2.329951810515372,4.094915062380427,7.196856730011514,12.648552168552959,22.229964825261955,39.06939937054613,68.66488450042998,120.67926406393264,212.09508879201925,372.7593720314938,655.1285568595496,1151.3953993264481,2023.5896477251556,3556.4803062231213,6250.551925273976,10985.411419875572,19306.977288832455,33932.217718953296,59636.23316594637,104811.3134154683,184206.99693267164,323745.754281764,568986.6029018281,1000000.0],[1e-06,1.757510624854793e-06,3.0888435964774785e-06,5.428675439323859e-06,9.540954763499944e-06,1.67683293681101e-05,2.94705170255181e-05,5.1794746792312125e-05,9.102981779915228e-05,0.00015998587196060574,0.0002811768697974231,0.0004941713361323833,0.000868511373751352,0.0015264179671752333,0.0026826957952797246,0.004714866363457394,0.008286427728546842,0.014563484775012445,0.025595479226995333,0.04498432668969444,0.07906043210907701,0.1389495494373136,0.244205309454865,0.42919342601287785,0.7543120063354607,1.325711365590108,2.329951810515372,4.094915062380427,7.196856730011514,12.648552168552959,22.229964825261955,39.06939937054613,68.66488450042998,120.67926406393264,212.09508879201925,372.7593720314938,655.1285568595496,1151.3953993264481,2023.5896477251556,3556.4803062231213,6250.551925273976,10985.411419875572,19306.977288832455,33932.217718953296,59636.23316594637,104811.3134154683,184206.99693267164,323745.754281764,568986.6029018281,1000000.0],[0.0006015170467586964,5357.645905431237,0.008579956814279222,0.002622938701902548,0.0034474437049411173,0.006440480639129858,0.0071292854503499405,0.0012445306696626736,0.0013349353055128505],[0.0006015170467586964,5357.645905431237,0.008579956814279222,0.002622938701902548,0.0034474437049411173,0.006440480639129858,0.0071292854503499405,0.0012445306696626736,0.0013349353055128505]],"z":[[[0.44356211245639154,0.44035889816806517,0.4373301195029345,0.43450272287353686,0.4319030899352514,0.4295564676688926,0.4274863601513361,0.42571390383191954,0.42425725387198276,0.42313101357554045,0.4223457411427148,0.4219075670185117,0.42181795045350506,0.4220735956048114,0.42266653636607987,0.42358438653741953,0.4248107396869993,0.42632569280542376,0.42810646084967313,0.4301280460675463,0.43236392643742144,0.43478673096482146,0.43736887497834726,0.4400831349615122,0.44290314898880534,0.44580383488283915,0.44876172340029763,0.45175520792276747,0.4547647152633987,0.45777280438707235,0.4607642012157752,0.46372577840384327,0.46664648916651563,0.469517264060868,0.47233087916068334,0.4750818034252826,0.47776603230627357,0.48038091381878223,0.4829249724645405,0.48539773556220234,0.487799565736488,0.49013150255693727,0.4923951156096385,0.4945923706382478,0.4967255098085742,0.4987969466364734,0.5008091756728852,0.5027646966622236,0.5046659525794454,0.5065152807044508],[0.44145510641767477,0.43812252784846845,0.43496790884692826,0.43202007651153623,0.42930738920742517,0.42685711024758977,0.4246947295124159,0.42284325691447927,0.4213225193256092,0.4201484990725748,0.41933275596282177,0.4188819746389181,0.4187976739292991,0.41907610465818834,0.4197083480840782,0.4206806107447995,0.42197469554761646,0.4235686158971657,0.4254373112121557,0.42755341897768007,0.42988806009956976,0.43241159962399967,0.4350943524093774,0.43790721170708313,0.4408221867402699,0.44381284256172443,0.44685464136725433,0.449925188951854,0.4530043932056058,0.45607454363057964,0.4591203220280333,0.46212875496303124,0.46508911854493284,0.46799280562018847,0.47083316478097187,0.47360531974329695,0.47630597671194175,0.47893322637809815,0.4814863462260057,0.48396560788276904,0.4863720933490975,0.48870752311001425,0.4909740983520738,0.49317435881258653,0.49531105716031315,0.4973870502577362,0.4994052071828503,0.5013683334925702,0.503279110888446,0.5051400511951504],[0.43971240847714294,0.43625748603630965,0.43298321255022154,0.4299203093591263,0.4270991552732326,0.4245491030283398,0.4222977265830518,0.42037002477893537,0.418787617111982,0.4175679766446678,0.4167237514514726,0.4162622273163633,0.4161849790322551,0.41648774511360453,0.4171605422293725,0.4181880140373335,0.41954998813058836,0.4212221980918167,0.4231771175721427,0.42538485052477953,0.42781402530600793,0.43043264841172657,0.43320888399356755,0.4361117361258876,0.43911162075915144,0.4421808226629541,0.4452938391709506,0.4484276172432688,0.4515616934848844,0.45467824859401573,0.45776208855782513,0.46080056502630024,0.46378344689667605,0.4667027544004507,0.4695525660321017,0.472328807587341,0.47502903145633174,0.4776521931906353,0.4801984312637532,0.4826688548951244,0.4850653438205343,0.48739036297735916,0.4896467942367436,0.49183778656071725,0.49396662529276414,0.4960366207065025,0.49805101543922636,0.5000129100237447,0.5019252054012658,0.5037905610461668],[0.43838562446608637,0.4348179008032398,0.43143256193596347,0.4282622038494278,0.42533923969853477,0.4226951601875002,0.42035970394343897,0.41835996410570303,0.41671947069855164,0.4154573014266221,0.4145872836518658,0.4141173542627144,0.41404913908546526,0.414377798173246,0.4150921591216428,0.41617513161841935,0.41760436847252397,0.4193531168066024,0.4213911912758956,0.4236859995979784,0.42620355745974103,0.42890944190170927,0.43176964641133414,0.4347513147394039,0.43782334239511317,0.44095684423064346,0.44412549344329477,0.4473057419830046,0.4504769351732812,0.453621334766734,0.45672406504740687,0.45977299627551066,0.4627585789879091,0.4656736415992263,0.468513162521283,0.47127402672167606,0.47395477533556357,0.47655535566715923,0.47907687769437696,0.48152138203707257,0.48389162327584595,0.4861908715206467,0.4884227342298663,0.4905909994741049,0.4926995011257824,0.4947520058372694,0.49675212114633804,0.49870322361739217,0.5006084055877507,0.5024704388365573],[0.43752810422159144,0.4338599781067425,0.43037490886264024,0.4271073059271887,0.42409159135187957,0.4213614079311594,0.4189487125249938,0.41688277997134987,0.4151891600195546,0.4138886477991515,0.41299634398584806,0.41252088925180214,0.41246395395788393,0.41282004558661606,0.41357666447485564,0.414714799028268,0.4162097137303689,0.4180319552778859,0.42014848876577954,0.4225238769288277,0.4251214273475023,0.42790425019685974,0.43083618804650264,0.43388259637119486,0.4370109673115483,0.44019139948866437,0.44339692364943445,0.44660369820766965,0.4497910910027388,0.45294166440222444,0.4560410806929762,0.45907794388681383,0.4620435928650292,0.464931859374848,0.4677388028891938,0.47046243282506717,0.4731024271339937,0.47565985485954415,0.4781369089184212,0.48053665411256385,0.4828627942245819,0.48511946099070163,0.4873110267858149,0.489441941996034,0.49151659729667646,0.49353921039923854,0.4955137362800344,0.4974437994553592,0.49933264652099346,0.5011831169238922],[0.4371942775592796,0.43344134256349215,0.42987097972038785,0.4265193001601853,0.42342265916657296,0.42061681927535377,0.41813597000342784,0.4160116264752906,0.41427145029036594,0.4129380604133214,0.4120279254629796,0.4115504446229569,0.41150732439704313,0.41189233678185794,0.41269150180165576,0.4138836827259769,0.4154415300721538,0.41733267401990676,0.41952105065036743,0.42196825378170355,0.42463482411244036,0.4274814128349623,0.4304697816504002,0.4335636217832933,0.43672919005030003,0.43993577057177385,0.4431559772287196,0.4463659154807343,0.44954522357483173,0.4526770131987697,0.4557477287830336,0.4587469432932792,0.4616671067217143,0.46450326173880413,0.4672527392043961,0.4699148445194016,0.4724905441588467,0.4749821601820386,0.47739307907323625,0.4797274799290765,0.48199008577733415,0.4841859406852258,0.4863202142948486,0.4883980345097856,0.49042434825256387,0.49240380951958185,0.49434069338006525,0.496238834098936,0.4981015852086148,0.49993179910790336],[0.4374388212293931,0.4336201950456622,0.4299824340167461,0.4265631798478158,0.4234005834396959,0.420532434135915,0.4179951141149517,0.4158223938962957,0.4140441098641756,0.4126847966744676,0.4117623820182411,0.411287079068382,0.4112606197375772,0.4116759479032348,0.41251743428065585,0.41376159708775645,0.41537823910972477,0.4173318641916216,0.419583223345828,0.422090856914049,0.42481253148632747,0.42770650601886867,0.43073259291295707,0.4338530035878856,0.4370329842683475,0.4402412576715379,0.44345029168470107,0.4466364184314432,0.44977982744763517,0.4528644558064294,0.4558777964689299,0.4588106442280224,0.4616567965672928,0.46441272470103284,0.4670772280671863,0.469651083651096,0.4721366997413343,0.474537782064397,0.4768590187114953,0.47910578885368926,0.4812838989374964,0.48339934885932156,0.4854581295334522,0.4874660522968381,0.4894286097379447,0.49135086680062123,0.49323738040080545,0.495092145305924,0.49691856366346476,0.49871943532279733],[0.4383156442188355,0.4344542686941815,0.430770802973708,0.4273041814086211,0.4240941393765085,0.4211803239487017,0.418601197049571,0.4163927368930805,0.4145869710909369,0.41321041465237845,0.41228253506818713,0.4118144133187856,0.4118077929811339,0.41225468649324154,0.41313762951233696,0.4144305611673259,0.4161002018693504,0.41810773874580043,0.4204106225190106,0.42296431375990506,0.4257238669201014,0.4286452889224873,0.4316866467214979,0.43480892377175695,0.43797664082888016,0.4411582648101104,0.4443264330539429,0.447458021054061,0.4505340808154023,0.4535396751541788,0.45646363100588977,0.45929823239246825,0.46203887129004223,0.46468367231921076,0.46723310499243176,0.4696895952148474,0.4720571458463185,0.4743409743870231,0.4765471742362443,0.4786824044844116,0.4807536118242041,0.4827677869039607,0.4847317562955565,0.48665201021300436,0.48853456520321187,0.4903848602436897,0.49220768402997955,0.4940071307224566,0.4957865810489873,0.4975487054233071],[0.4398766860220449,0.4359995712655206,0.4322961882826133,0.4288064548232073,0.4255713964125167,0.42263225711362623,0.4200293717661045,0.41780079129825065,0.41598068032138574,0.4145975522903867,0.41367247324340767,0.4132174397042165,0.41323418908316834,0.4137136873633908,0.414636432435899,0.41597354078880044,0.4176884275678759,0.4197388123726045,0.42207879521119157,0.4246608121870256,0.42743735619762085,0.43036240980776347,0.43339257926174485,0.4364879432976688,0.43961264327314775,0.4427352466172741,0.4458289168995391,0.448871422784311,0.4518450159541969,0.4547362053811426,0.45753545245786165,0.46023680866706707,0.46283751476148494,0.46533757789924907,0.4677393408417158,0.4700470551703453,0.47226646850308196,0.4744044338709621,0.47646854773480773,0.4784668215645317,0.48040739045947695,0.48229826095241296,0.4841470989137846,0.4859610573625837,0.487746643006071,0.48950961948353644,0.4912549445901694,0.4929867382135711,0.4947082773302652,0.49642201418044657],[0.44217053398973527,0.43830891292070445,0.434615711120315,0.43113144953126736,0.42789806109130407,0.4249580217733401,0.42235321732482656,0.4201235202014906,0.41830507455596905,0.4169283344856665,0.41601598184309724,0.4155809621456023,0.4156249828349974,0.416137835722144,0.4170977623743773,0.41847281314120816,0.420222908219313,0.422302218407731,0.42466153871931184,0.42725044424204395,0.43001912424651434,0.43291986279980893,0.4359081751506986,0.43894362934400216,0.44199039075381114,0.44501752913334436,0.44799912654203405,0.450914221817242,0.45374662398059684,0.45648462354993097,0.45912062738779363,0.4616507395625018,0.4640743077729008,0.4663934522049029,0.46861259123899696,0.4707379761943659,0.47277724525200837,0.4747390048199077,0.4766324448626191,0.4784669930955919,0.48025201142784646,0.4819965366203472,0.4837090658149278,0.48539738639056934,0.48706844853554854,0.488728278003097,0.49038192576104883,0.49203345066458315,0.493685930881638,0.4953414995805922],[0.44524088236157566,0.44143023611235277,0.4377817190340663,0.4343360110498585,0.4311354835832803,0.42822336938533545,0.42564265097858756,0.42343462490247613,0.4216371132941606,0.42028233405877985,0.41939452768442426,0.418987592238766,0.4190631718069724,0.4196097427048473,0.42060305978325846,0.4220078828290804,0.4237805163468446,0.4258716131805052,0.4282288427336453,0.4307992165593569,0.4335309990641103,0.43637520346468583,0.4392867057445432,0.44222502142246956,0.4451547924272499,0.4480460296544755,0.4508741533591302,0.45361986953753747,0.4562689163801761,0.45881171095758433,0.46124292263321726,0.4635609963175991,0.46576764559535916,0.46786733296076966,0.4698667518668785,0.4717743229983992,0.47359971508522436,0.4753533986461448,0.47704623925886247,0.4786891352666766,0.48029270323811546,0.48186701298826023,0.4834213725562856,0.48496416222915983,0.48650271552977703,0.4880432440750792,0.48959080238007374,0.4911492880553432,0.49272147242828634,0.4943090564105542],[0.4491248771840472,0.4454047890998475,0.4418397856252002,0.43847021158957705,0.43533833379679715,0.43248756267726873,0.4299613858747542,0.42780195715873365,0.426048286718287,0.4247340010715405,0.4238847124961096,0.42351521451159746,0.4236270372059928,0.4242071859425091,0.42522869738737495,0.4266528728237757,0.4284324067219352,0.4305146320853894,0.4328444431547354,0.43536673661612435,0.43802835334063994,0.44077955765593324,0.443575108301562,0.4463749777741177,0.44914477405490083,0.45185591426219884,0.45448559490131496,0.4570165985882306,0.4594369725783549,0.4617396102057175,0.4639217624522563,0.46598450332568714,0.46793216951965655,0.4697717919440136,0.4715125341180846,0.4731651500788837,0.474741472326343,0.47625393836386054,0.4777151625529404,0.4791375582522121,0.4805330135331154,0.48191262215201564,0.4832864699223818,0.48466347519535447,0.48605128085664606,0.4874561941196637,0.4888831694740205,0.49033582946175513,0.491816517514764,0.49332637689552516],[0.4538514166799558,0.45026521625857147,0.44682657608060683,0.4435749816073036,0.4405519993843074,0.4378005552939261,0.43536392705128246,0.4332843866474604,0.4316014214303437,0.4303494638842485,0.42955509370408657,0.42923381942184696,0.42938697095467754,0.42999991380451885,0.4310427615962151,0.4324733185362399,0.4342408856682914,0.4362898989613649,0.43856302087111676,0.441003629601218,0.443557750127589,0.44617549386001654,0.4488120749416231,0.45142846664887964,0.453991755572003,0.4564752454462552,0.45885835698786037,0.4611263649323516,0.46327000868437496,0.465285008565168,0.46717151558799347,0.4689335190052338,0.47057823254896863,0.47211547731446146,0.4735570765835898,0.47491627550975485,0.47620719643366655,0.4774443386130117,0.4786421292734474,0.47981453107975397,0.48097470935721093,0.4821347606589375,0.48330550259130983,0.48449632321219455,0.48571508685449366,0.4869680919536579,0.48826007542222905,0.48959425735456474,0.4909724193808239,0.49239500982086787],[0.45943950228412267,0.45603367324943755,0.45276769796126953,0.4496796686611359,0.4468098300987404,0.44419991091231,0.4418921765656289,0.43992813716356755,0.4383468320634228,0.43718260203366266,0.43646225577672654,0.43620158593875896,0.436401550554361,0.43704569797002407,0.4381011143095712,0.4395223306952952,0.4412557782243598,0.44324367040010065,0.4454271571474555,0.4477488087767285,0.4501545138441735,0.452594871505136,0.45502615177750166,0.4574108899548781,0.45971817477386717,0.46192368383159854,0.4640095140784829,0.465963849910746,0.4677805064299339,0.46945838082547353,0.4710008405902402,0.4724150734201282,0.4737114201878347,0.47490270931157086,0.47600360813188036,0.4770300045127087,0.47799842972858697,0.4789255317121653,0.4798276058417002,0.4807201885865097,0.4816177174631771,0.4825332588791331,0.48347830357669225,0.4844626275906132,0.48549421496465966,0.486579237013449,0.48772208173461784,0.48892542612563805,0.4901903436668096,0.4915164390966821],[0.46589675556980764,0.46272010573447964,0.45967570248361617,0.4567997167052668,0.45413044665398267,0.4517076936718473,0.4495718679732414,0.44776275759027995,0.44631788124331095,0.4452703320445299,0.4446460036478474,0.44446007630254514,0.4447127241897928,0.4453855174573023,0.44644270926063445,0.44783622316114097,0.449510478352318,0.45140633934347324,0.45346427172989917,0.45562680676070877,0.4578404072488204,0.4600568179210296,0.4622339751572222,0.46433654390280055,0.4663361430544451,0.4682113145936965,0.46994728604008124,0.4715355703566134,0.47297344226710847,0.4742633250769199,0.47541211758350393,0.4764304865740879,0.4773321467695372,0.47813314688991426,0.47885117775874453,0.47950491596582767,0.4801134144839661,0.48069554968062506,0.48126953228042335,0.48185248793492874,0.48246011109120646,0.4831063938089643,0.4838034290915504,0.4845612862398026,0.4853879538077964,0.48628934404271484,0.48726935132470917,0.4883299561593055,0.48947136575121425,0.49069218210172577],[0.4732182232321127,0.47032084557884823,0.4675484308464903,0.46493471145707993,0.4625154216717372,0.4603277069116829,0.4584092713208081,0.4567971966476172,0.45552635278098064,0.45462730592607403,0.45412361440110854,0.4540283843195019,0.4543399544663793,0.4550378806501164,0.45608443742381155,0.4574300412501004,0.4590181465577406,0.4607892181775229,0.46268389542755084,0.46464545120850453,0.4666216388327696,0.4685660105022936,0.47043878383310395,0.47220732614567706,0.4738463200523306,0.47533766794353116,0.47667018718593834,0.47783914217434953,0.47884565387860417,0.4796960222893827,0.48040099230200467,0.48097498918094667,0.4814353458834334,0.48180154120609997,0.4820944649211275,0.4823357237069374,0.48254699963415476,0.4827494711004814,0.48296330427817685,0.48320722122766885,0.4834981487665453,0.4838509499483897,0.4842782376464386,0.4847902673538521,0.4853949040436698,0.4860976559278702,0.4869017663525338,0.48780835396395,0.48881659072611844,0.4899239073561449],[0.48138557978866353,0.4788176672799241,0.47636789394627754,0.47406704374329384,0.4719476738142371,0.4700435460992244,0.4683888049809107,0.46701683401401484,0.4659587116086224,0.46524117087914046,0.4648839538556143,0.4648964473325909,0.4652736764936176,0.4659932496509694,0.46701665638154666,0.46829400003491184,0.4697688350245012,0.47138217698205254,0.4730756965428409,0.4747941910366516,0.47648742606829775,0.478111431991467,0.47962933371249855,0.4810117861887157,0.48223708211849614,0.48329099244123835,0.4841663942899741,0.4848627350012329,0.4853853748068513,0.4857448450784455,0.48595605364354705,0.4860374638936282,0.4860102702582804,0.4858975891603346,0.48572368175518316,0.4855132224878165,0.4852906256127377,0.48507944012290116,0.48490182182867103,0.48477808945067263,0.48472636943381914,0.48476233172780486,0.484899016074481,0.48514674553687165,0.4855131212940751,0.4860030903236159,0.4866190756881272,0.48736115787114026,0.4882272950273946,0.4892135701082176],[0.4903668039298472,0.4881774048401167,0.48609982067558616,0.4841613777907156,0.482390840975059,0.48081785592009413,0.47947214579596265,0.47838239574967056,0.47757474685031187,0.4770708108363538,0.47688512214049456,0.4770220281525193,0.47747243242303056,0.47821184387933285,0.47920149934451944,0.480392121958786,0.48172834358478694,0.48315265225440873,0.4846086025553375,0.48604330640844845,0.4874092783055597,0.4886657168120759,0.489779302031759,0.4907245843625973,0.49148403467533663,0.4920478202725108,0.49241336473731806,0.4925847432174728,0.4925719580433616,0.49239013312609153,0.4920586595861493,0.49160031974881385,0.49104041215309885,0.49040589660809764,0.48972457554693727,0.4890243258333167,0.4883323935524979,0.48767476290435763,0.4870756088385524,0.48655684129501664,0.4861377466804615,0.4858347294805804,0.4856611537628842,0.48562728096705016,0.4857402970869142,0.4860044194224437,0.48642107078739466,0.4869891075809837,0.4877050875424513,0.4885635632678095],[0.5001163548332734,0.49835216218648715,0.49669391766631166,0.4951649819599331,0.49378971300396035,0.4925929099030475,0.4915990219703563,0.4908310610883336,0.49030914881406623,0.49004863504275126,0.4900577709092759,0.49033507960372635,0.49086695954223064,0.4916265584382379,0.4925748276721669,0.4936635283397067,0.4948390638521968,0.49604618185410554,0.49723111684860555,0.49834406957434396,0.4993410463454083,0.500185122666007,0.5008472067247507,0.5013063794290656,0.5015498846069759,0.5015728378719811,0.5013777162251483,0.5009736832745928,0.5003757974536991,0.4996041432630412,0.49868291874693005,0.4976395064594714,0.4965035502789673,0.4953060566663083,0.49407853627238124,0.4928521999963711,0.4916572223918396,0.4905220843526745,0.48947300590880116,0.48853347838633027,0.48772390290892387,0.4870613391655771,0.4865593646579677,0.486228040551083,0.4860739761826003,0.48610048066998807,0.48630778726297286,0.4866933343683021,0.4872520866063404,0.4879768797699488],[0.5105758208666427,0.5092800763984909,0.5080847799920674,0.5070088311532843,0.5060715853659935,0.505292295550334,0.5046893370428731,0.5042791651161279,0.5040749573675316,0.5040849184521704,0.5043102999329108,0.5047433553430895,0.505365714620517,0.5061478593530268,0.5070501829028761,0.5080254949422286,0.5090223024076792,0.509988158943304,0.5108726365474059,0.5116297296442487,0.5122196532718926,0.5126100687357008,0.5127768001800235,0.5127041162831023,0.5123846527877223,0.5118190482051054,0.5110153588362141,0.509988311461707,0.5087584435599314,0.5073511724614581,0.50579582703931,0.5041246688132405,0.5023719239907424,0.5005728440772241,0.4987628101871426,0.49697649483828144,0.4952470944328282,0.4936056453411206,0.49208043598682494,0.4906965261089983,0.4894753821069458,0.4884346339387152,0.4875879545913818,0.4869450580720257,0.48651180675630534,0.4862904143962418,0.48627972765684635,0.48647556705092765,0.4868711076576596,0.4874572809016972],[0.5216749683577397,0.5208865336003277,0.5201933124923429,0.5196092815351457,0.5191482461072688,0.5188232829043717,0.5186459950971627,0.518625546056929,0.5187674510328485,0.5190721442079607,0.5195334185714503,0.5201369679197909,0.5208594102879296,0.521668226932641,0.5225228793112577,0.5233770009098955,0.5241812397859302,0.5248862432025153,0.5254453913776211,0.5258170592968752,0.5259663227403595,0.5258661095772659,0.5254978430207162,0.5248516451422732,0.5239261765997077,0.5227281879668606,0.5212718525681403,0.5195779424221373,0.5176728993082136,0.5155878432504598,0.513357551747325,0.5110194354843696,0.5086125304230289,0.506176522194246,0.5037508165516273,0.5013736689560105,0.499081386686741,0.4969076175719995,0.49488273979280395,0.4930333665655956,0.49138197733898104,0.4899466832475388,0.4887411291359554,0.4877745280691952,0.4870518177129144,0.4865739222020338,0.48633809886236706,0.4863383468460856,0.4865658544527645,0.4870094633764828],[0.5333330921018006,0.5330857066586211,0.5329284864655868,0.5328700818116492,0.5329182786839092,0.5330794516217978,0.5333578695151108,0.5337548398799236,0.5342676971053476,0.5348886808161174,0.5356038181894012,0.5363920124232506,0.5372246134280485,0.538065741610283,0.5388735021063614,0.5396019999885935,0.5402038642973813,0.5406329094615496,0.5408466094522902,0.5408081688837441,0.5404880854006533,0.5398651812592397,0.5389271358152921,0.537670580804162,0.5361008338592792,0.5342313481736116,0.532082951541076,0.5296829391434541,0.5270640735836383,0.5242635344840398,0.521321849694347,0.5182818316127735,0.5151875357957925,0.5120832550836993,0.5090125607997849,0.5060174028326585,0.5031372819862916,0.5004085100706825,0.4978635748551568,0.4955306272574067,0.4934331062281071,0.4915895123598416,0.4900133345196119,0.48871312558530133,0.4876927148822751,0.48695153748933784,0.48648505528382785,0.48628524199450385,0.4863411046315155,0.4866392160062761],[0.5454605644884766,0.5457822837854073,0.5461892661205834,0.5466845135812278,0.5472694259194735,0.5479432756428799,0.5487025846720748,0.5495404073066203,0.5504455459046315,0.5514017613650729,0.5523870896167364,0.5533734268898306,0.5543265746588449,0.5552069062114197,0.5559707146505325,0.556572153673459,0.5569655500939523,0.5571078049620574,0.5569606184914695,0.5564923446481607,0.5556793671263445,0.554506964381255,0.5529696872420304,0.551071307732459,0.5488244154155064,0.5462497421558387,0.5433752917612511,0.5402353410503367,0.5368693663729287,0.5333209366883287,0.5296366025631176,0.5258648009103736,0.5220547885220947,0.5182556136425684,0.5145151338784122,0.5108790902385061,0.5073902503450614,0.504087637855064,0.5010058686243057,0.49817461578117395,0.49561822448551607,0.49335549210513274,0.49139962107319407,0.48975834094280535,0.48843418495222474,0.48742489672964,0.48672393614737175,0.48632105051253816,0.48620287810477764,0.4863535547353718],[0.557960492528426,0.5588732796673996,0.559866577478261,0.5609375155918446,0.562080857822971,0.5632885098163763,0.5645489813636775,0.5658468249540767,0.5671620919623179,0.5684698750364182,0.5697400360483614,0.5709372432080848,0.5720214420605798,0.5729488469581029,0.5736734593548025,0.5741490165948591,0.5743311856287647,0.5741797717030268,0.5736607219773157,0.5727477553078344,0.5714235193511178,0.5696802446009153,0.5675199199116718,0.5649540509776749,0.5620030826007382,0.5586955704605666,0.5550671825455017,0.5511595984475489,0.547019359867307,0.5426967106126058,0.5382444509883095,0.533716820922673,0.5291684190550695,0.5246531615083321,0.5202232840606544,0.515928394500701,0.5118145873389582,0.5079236395879418,0.5042923124085342,0.5009517871534037,0.4979272639220623,0.4952377450590513,0.49289601522011534,0.4909088153298935,0.48927719271311865,0.4879969969032282,0.4870594823794261,0.4864519766529691,0.48615857423032854,0.48616082262348487],[0.570730414275556,0.5722498538937992,0.5738452403392719,0.5755077136111761,0.5772252750621877,0.5789823335694011,0.5807592601161256,0.5825319863924597,0.5842716992816762,0.5859447011667904,0.587512521334725,0.5889323684650605,0.5901579985966913,0.5911410304154435,0.5918326728972243,0.5921857543648046,0.5921568796702218,0.5917085131836398,0.5908107967232131,0.5894429565383897,0.5875942164726339,0.5852641990202316,0.582462849866598,0.5792099582691098,0.5755343641566497,0.5714729455677087,0.5670694713093577,0.5623733881940611,0.5574385940314696,0.552322229845105,0.5470835096018737,0.5417825942384824,0.5364795094539584,0.5312331037211493,0.5261000441098016,0.5211338524349887,0.5163839922321362,0.5118950268604399,0.507705878688944,0.5038492262106452,0.5003510772711451,0.4972305503739559,0.4944998820792959,0.49216465914108803,0.4902242534750402,0.488672420996095,0.487498015155666,0.48668576365602456,0.4862170611376534,0.4860707392122095],[0.5836639908250008,0.5857990949380967,0.5880058277224851,0.5902693322605491,0.5925708437715337,0.5948872745326663,0.5971908584273643,0.5994489025309301,0.6016237055795852,0.6036727132727097,0.6055489836320094,0.607202026288815,0.608579052339889,0.6096266247955207,0.6102926390263085,0.610528500888407,0.61029132414862,0.6095459524294158,0.6082666293952875,0.6064381890082898,0.6040567024128205,0.6011295840182374,0.5976752138509689,0.5937221688627593,0.5893081710430992,0.5844788578053945,0.5792864655066434,0.5737884958676647,0.5680464123653943,0.5621243928091904,0.5560881473013621,0.5500037985322755,0.5439368141105033,0.5379509783019643,0.532107392973274,0.5264635044557844,0.5210721639661549,0.5159807430037078,0.5112303395856791,0.5068551227833799,0.5028818674763429,0.49932972488214655,0.4962102562879509,0.49352773068001876,0.4912796583463831,0.4894575095073435,0.48804755463489047,0.4870317622461766,0.4863886979987455,0.48609438176791725],[0.596652671843845,0.5994057554013223,0.6022264502225637,0.6050940025703262,0.6079829962464203,0.6108629706452553,0.6136981446912715,0.616447304460224,0.6190639217163141,0.621496574714558,0.623689737043151,0.6255849805274547,0.6271226014969528,0.6282436272941267,0.6288920988887851,0.6290174685411141,0.6285769137208883,0.6275373621381137,0.6258770520526276,0.6235865112100563,0.6206689128179609,0.617139840769559,0.6130265542076265,0.6083668753151303,0.6032078331000377,0.5976041847215241,0.5916169120701591,0.5853117623088835,0.5787578726487805,0.5720264953096897,0.5651898200187532,0.5583198788650807,0.5514875115647143,0.5447613677863727,0.5382069269046558,0.5318855243652789,0.5258533877302692,0.5201607037839665,0.5148507587083346,0.5099592118808994,0.5055135737559955,0.5015329528950042,0.4980281135951385,0.49500184794581525,0.49244962541246873,0.4903604516319501,0.4887178536330372,0.4875009112634036,0.48668526878116336,0.48624407947595716],[0.6095873284653786,0.6129539429345716,0.616384483561348,0.6198525004670653,0.6233261518744824,0.6267678447188002,0.6301340205203814,0.6333751539825571,0.6364360397067488,0.6392564429840518,0.6417721792546791,0.6439166593529397,0.6456228921531513,0.6468258752184946,0.6474652360544118,0.6474879257872916,0.6468507302998701,0.6455223648330606,0.6434849615992673,0.6407348384743147,0.6372825320332123,0.6331521674545346,0.6283803023944108,0.6230144127167707,0.6171111864441339,0.6107347672852528,0.6039550519258353,0.5968461058348431,0.5894847272244077,0.5819491611845056,0.5743179465669759,0.5666688662168462,0.5590779655174063,0.5516186040153017,0.544360509767346,0.5373688162966401,0.5307030783848052,0.5244162857969019,0.5185539221714811,0.5131531448357958,0.5082421806586868,0.5038400312198036,0.4999565500733065,0.4965929007561025,0.49374234474325035,0.4913912652510816,0.48952031729368983,0.4881056041624702,0.487119804505434,0.48653320125376576],[0.6223598562347297,0.6263287808439431,0.6303582672143982,0.6344164600121753,0.6384654190979495,0.6424607687725263,0.6463515231746534,0.6500801645184047,0.6535830591881736,0.6567912965041637,0.6596320209982037,0.6620302963836932,0.6639114854914862,0.6652040576445817,0.6658426528413728,0.6657711579290766,0.664945505488209,0.6633359107744581,0.6609283235818934,0.6577249801294328,0.6537440681935626,0.6490186332960775,0.6435949284813711,0.6375304350726336,0.6308917633007491,0.6237525960384719,0.6161917834479814,0.6082916441710402,0.6001364867021066,0.5918113347099923,0.5834008212268527,0.5749882065273276,0.5666544709270777,0.5584774350874213,0.5505308661848374,0.5428835391043152,0.5355982393347407,0.5287307206690522,0.5223286670565925,0.5164307501405536,0.5110659093944396,0.5062529892567986,0.5020008293985115,0.4983088244048582,0.4951678796892268,0.49256163035585177,0.4904677766454862,0.4888594135133092,0.4877062709970107,0.4869758191915052],[0.6348647526824234,0.6394180535316172,0.6440288019920617,0.6486601036753287,0.6532683359439588,0.6578027906759,0.662205514224256,0.6664114298020675,0.6703488383277454,0.6739403958766709,0.6771046529852447,0.6797582064294017,0.6818184528583555,0.6832068461954736,0.683852456626596,0.6836955295263865,0.6826906785438007,0.6808093491003994,0.6780412723711868,0.6743947824402733,0.6698960489620535,0.6645874311071316,0.65852524639138,0.6517772602313889,0.6444201557239373,0.6365371672670669,0.6282159825029077,0.6195469507695474,0.6106215886553619,0.6015313434458824,0.5923665593196977,0.5832155847195054,0.5741639588787182,0.5652936188252795,0.5566820745610177,0.5484015103326825,0.5405177865389844,0.5330893442079094,0.5261660569702664,0.5197881345048545,0.5139852429211539,0.5087760365844141,0.504168251540533,0.5001593894812176,0.4967378813830913,0.4938845366650775,0.49157408223835297,0.4897766462239836,0.488459101738592,0.48758623376792226],[0.6470006696856154,0.652113845660251,0.6572814662202472,0.6624620218666339,0.6676066952899027,0.6726589838937385,0.6775545297326643,0.6822212491607823,0.6865798697255086,0.6905449895428117,0.6940267669854717,0.6969333165652238,0.6991738212885821,0.7006622682292812,0.7013215797089858,0.7010877722964197,0.6999136737659472,0.6977717157857677,0.6946554305723421,0.6905794989231676,0.685578457340244,0.6797043838532268,0.6730239838475545,0.6656154827243255,0.6575656401255643,0.6489670816215302,0.6399160359924299,0.6305104868117452,0.6208486975188314,0.611028043407793,0.6011440740550311,0.5912897289614327,0.5815546329870291,0.5720244038995572,0.5627799111554515,0.553896433658644,0.5454426775911824,0.537479639505192,0.5300593445819539,0.5232235654652229,0.5170027275782871,0.5114152821797677,0.506467788410961,0.502155755640552,0.49846506849827865,0.49537370432337186,0.4928534856133229,0.4908717068999298,0.48939256242106344,0.48837835528630963],[0.6586719310752809,0.6643141713342964,0.670007754707113,0.6757070160562921,0.6813584816309597,0.6869004616578076,0.6922628494792034,0.697367223885738,0.7021273723980802,0.7064503696775345,0.7102383484475936,0.7133910776383385,0.7158093986756766,0.7173994532321147,0.718077464074387,0.7177746302936507,0.7164415297687786,0.7140513718356454,0.7106015823682379,0.7061135239867716,0.7006305434456188,0.6942148379308002,0.686943741944849,0.6789059668000127,0.6701981584514863,0.660921962559865,0.6511816476529431,0.6410822502724796,0.6307281615911677,0.6202220588534905,0.6096640845725664,0.5991511830889023,0.5887765128382919,0.5786288610211164,0.5687919945602216,0.5593438878870792,0.5503557765868925,0.5418910021555954,0.5340036502385701,0.5267370667468587,0.5201224845265062,0.5141781603756076,0.5089094236961346,0.5043097308084762,0.5003624220195786,0.4970427395909864,0.4943197844845717,0.4921582585539153,0.4905199474525741,0.48936494990807405],[0.6697899923358652,0.6759245719521905,0.6821070229282675,0.6882879943421624,0.6944099179624502,0.7004065677599376,0.7062028149238708,0.7117146752438827,0.7168497731176532,0.7215083739239159,0.7255851555779121,0.7289718852791164,0.731561115979123,0.7332508934169459,0.7339502531898383,0.7335850051008973,0.732103024429383,0.7294781374643889,0.725711849621728,0.720832642002157,0.7148931651994259,0.7079660912852626,0.7001394802155274,0.6915123365647328,0.6821907499601891,0.6722847649778032,0.6619059650687165,0.651165673448366,0.6401736452625628,0.6290371251629696,0.6178601562644223,0.606743041246739,0.5957818698506924,0.5850680376399205,0.5746876884619094,0.5647210181086164,0.5552413806777899,0.5463141457278433,0.5379952742827591,0.5303296466336963,0.5233493539465566,0.5170724888871764,0.5115031258537215,0.5066326739646403,0.5024420498640235,0.4989040013896052,0.49598522778328996,0.49364819288956374,0.4918526314157296,0.490556779232217],[0.6802748036098413,0.6868596405020678,0.6934881922226708,0.7001078758837093,0.7066575838209891,0.7130672150723912,0.7192573836282941,0.7251393952724886,0.7306156174091024,0.7355804054214242,0.7399217883224035,0.7435241392046575,0.7462720319111835,0.7480553720102935,0.7487756468355756,0.7483527578525737,0.7467314537264558,0.7438860835204649,0.7398225369989647,0.734576962848494,0.728211828321488,0.7208105157005037,0.712471664054537,0.7033040697480436,0.6934225076278004,0.6829445187173482,0.6719880498444,0.6606697760436989,0.6491039362281511,0.6374015332641136,0.6256697743241939,0.614011649224802,0.60252556131108,0.5913049373244307,0.5804377502627857,0.5700058933346575,0.5600843445570811,0.5507400616431374,0.5420305495950062,0.5340020680212667,0.5266875839659411,0.5201050739625532,0.5142573776316125,0.5091339872650322,0.5047137005115403,0.5009671907971945,0.4978592170347451,0.4953504606151407,0.49339903133856455,0.4919616889170637],[0.6900560221585125,0.697044408702421,0.704071342849818,0.7110814231336067,0.7180105191681871,0.7247852884318925,0.7313228475590631,0.7375306794608866,0.7433068924016254,0.7485409958722221,0.7531154189972674,0.7569080564497848,0.7597961487218718,0.7616617259999291,0.7623985919649987,0.761920342450065,0.7601682406712065,0.7571171609489414,0.7527778343638366,0.747194737116017,0.7404406111217422,0.7326095322673067,0.7238101914484142,0.714160264022091,0.7037820841587338,0.692799498656172,0.6813356625860336,0.6695115382117874,0.6574448956410971,0.6452496553650203,0.6330354476744231,0.6209072897697692,0.6089652992393937,0.5973043741856816,0.5860137771427303,0.5751765631786709,0.5648687929815865,0.5551584698108678,0.5461041354500484,0.5377530568624757,0.5301389647003961,0.5232797682925046,0.5171771950872397,0.511819187582382,0.5071829743663259,0.5032377508196918,0.49994690764319566,0.4972698658037126,0.49516357559354424,0.4935837303706567],[0.6990740093276722,0.7064155155562671,0.7137890949767931,0.7211368826916619,0.7283921772328553,0.735478962250314,0.7423115622415739,0.7487944989992803,0.7548226479307658,0.7602818461351761,0.765050183458665,0.7690003089539936,0.7720031733391689,0.7739336192563876,0.7746780020806222,0.7741434656992379,0.7722675727787706,0.7690258740611114,0.7644345929067901,0.7585472676900744,0.7514471623535653,0.7432385689093964,0.7340391533100491,0.72397406028696,0.7131716800354008,0.7017607242024481,0.689868256700928,0.6776183953699624,0.6651314730570594,0.6525235026173365,0.6399058290834683,0.6273848778091138,0.6150619236706161,0.6030328163302583,0.5913876020307183,0.5802099845964661,0.56957656798098,0.5595558202325611,0.5502066943772207,0.541576835527286,0.5337002956636229,0.5265948958449883,0.5202616593263718,0.5146876992375111,0.5098494357868386,0.5057152877248937,0.5022479015907195,0.49940598630478283,0.49714581168029104,0.49542242155461924],[0.7072805438784346,0.7149220668809694,0.7225876597581118,0.7302172848364759,0.7377420411682473,0.7450837128150799,0.752154437698409,0.7588565479543533,0.7650826578092519,0.7707161229242857,0.77563208269652,0.7796994379766196,0.78278429217993,0.7847554897151178,0.7854927162334996,0.7848969957668761,0.7829022943144947,0.7794852365471461,0.7746684273368418,0.768515148133883,0.7611189201028596,0.7525930271312755,0.7430623377794414,0.7326575493233035,0.72151129672102,0.7097555631261483,0.6975199727469612,0.6849306789076444,0.6721096516450278,0.6591742269160225,0.6462368148076391,0.6334046855790307,0.6207797652768756,0.6084583801643157,0.59653089304276,0.58508117569869,0.5741858607087879,0.5639133129774866,0.55432225686524,0.5454599894533444,0.5373601239265627,0.5300402216161195,0.5235013996119218,0.5177308675687073,0.5127050653207224,0.5083923618801178,0.5047552953156934,0.5017524171621912,0.499339799696743,0.4974722568241323],[0.714639192095982,0.7225261010575537,0.7304274421751242,0.7382812400680442,0.7460166893550585,0.753553747958908,0.7608028476884944,0.767664760374525,0.77403067209844,0.7797825513202338,0.7847939740357515,0.7889317314852134,0.7920588230206574,0.794039739042314,0.7947489081988388,0.7940823704295821,0.7919713155869913,0.7883942961117048,0.7833814333294022,0.777006011178707,0.7693705294209844,0.7605950282242195,0.7508091093299463,0.7401467345282923,0.7287428325736586,0.7167310600577642,0.7042423141739869,0.6914037491445562,0.6783381341795747,0.6651634383269275,0.6519925543135044,0.638933089015123,0.6260871573649806,0.6135511217403979,0.6014152213798956,0.5897630368298821,0.5786707332456507,0.5682060242661666,0.5584267978171829,0.54937936152918,0.5410963853172176,0.5335951358495441,0.5268773339523448,0.5209310808812778,0.5157336321959857,0.5112540283749629,0.5074553366998003,0.5042965104690359,0.5017339126423314,0.49972255220081685],[0.7211252978094125,0.7292026013992182,0.7372831026799902,0.7453030920785354,0.7531901030559411,0.7608625611434192,0.7682295566697002,0.7751907733825639,0.7816366093847338,0.787448539886331,0.7924998166633505,0.7966567383697007,0.7997810746590048,0.8017348412629087,0.8023890274916534,0.8016367838001366,0.7994088525743989,0.7956875829669555,0.7905117693993566,0.7839636598048624,0.7761519296802448,0.7672001749387921,0.7572398424810064,0.7464057906120259,0.734833374930488,0.722656468890794,0.7100061003723241,0.6970095159124081,0.6837895465419204,0.6704641806783203,0.6571462668893225,0.6439432796669979,0.6309570877243336,0.6182836681344099,0.6060127115981204,0.5942270648318941,0.5830019565131971,0.5724039562378604,0.5624896308951484,0.5533039204315764,0.5448784330766224,0.5372302186217255,0.5303617879372009,0.524262588802394,0.518911313788222,0.5142783201318348,0.5103278109136434,0.5070196893843657,0.5043110958417749,0.5021576623108827],[0.7267255917156484,0.7349390413003027,0.7431430406280688,0.7512723514919134,0.759253079128877,0.7670023789002122,0.7744282985376439,0.7814297891248544,0.7878969175667888,0.7937113111394412,0.798746870047584,0.802870844215137,0.8059456594989787,0.8078327893736958,0.8084014557835315,0.8075442658988625,0.8051958934699244,0.801346821386104,0.7960446493208484,0.7893772656665631,0.7814554414766608,0.7724027195069156,0.7623495549254394,0.7514295596318136,0.7397768975224822,0.7275244136522008,0.7148022840470148,0.7017370513873948,0.6884509459006811,0.6750614085395751,0.661680744379777,0.6484158414988742,0.6353678957049048,0.6226320850180096,0.6102971403505861,0.5984447613514291,0.5871488310880963,0.5764743955916866,0.5664764073312101,0.5571983116940751,0.5486707117051304,0.5409105374650214,0.5339211649602777,0.5276935910668513,0.5222083275254888,0.5174375355863728,0.5133470693222228,0.5098982803997504,0.5070495476394419,0.5047575425472048],[0.7314374640632857,0.7397345093386701,0.7480083448829357,0.756192443713378,0.7642117497862269,0.7719824387947568,0.779411826326966,0.7863984611430196,0.7928324424655065,0.7985959958986113,0.8035643281614341,0.8076067594907256,0.8105881957787036,0.8123717463537677,0.8128263108080679,0.8118454501127389,0.8093725814460363,0.805412315479422,0.8000206319724673,0.7932865931628234,0.7853186136228539,0.7762367806714368,0.7661681154321994,0.7552432014564584,0.7435936554810901,0.7313502190106014,0.7186413338254518,0.7055920950236416,0.6923234912150127,0.6789518524229425,0.6655884345832705,0.6523390760698896,0.639303866852196,0.6265767751710846,0.6142451808018542,0.6023892696181004,0.5910812544653348,0.5803844085471914,0.5703519403433273,0.5610258160734541,0.5524357443622318,0.5445986258590716,0.5375187339516888,0.5311886848906382,0.5255910025767134,0.5206999646749894,0.5164834606766485,0.5129047010269846,0.509923708311923,0.5074985760990056],[0.7352679879476651,0.7435985244530868,0.7518913488690325,0.7600789378297318,0.7680854032396234,0.7758263038766778,0.7832086128471218,0.7901308823958426,0.796483652208421,0.8021501491353736,0.8070073190355971,0.8109271982695134,0.8137785394944349,0.8154286018188287,0.8157479925436555,0.8146315316774911,0.8120342553604889,0.8079795101397875,0.8025316763512867,0.7957774360064682,0.7878193752021364,0.778771619680396,0.7687559260078358,0.7578984191879884,0.7463269913665008,0.7341692805387005,0.7215511296595323,0.7085954299253091,0.6954212603493615,0.6821432444701351,0.6688710528730681,0.6557089869670486,0.6427555853531439,0.6301031997241333,0.6178374936064243,0.6060368263172802,0.5947714995433355,0.5841028699867102,0.5740823744491854,0.5647505754041668,0.5561364024411325,0.548256799987841,0.5411169466554837,0.5347110796714293,0.5290238047859811,0.5240316834654708,0.5197048917957703,0.5160088028961106,0.5129054099886062,0.5103545565863143],[0.7382328096183542,0.7465496969475914,0.7548139997173013,0.7629575393029401,0.7709039849277315,0.7785687162264677,0.7858588470064888,0.7926734527488033,0.7989040505523948,0.8044353858123321,0.8091465821002344,0.8129126989852589,0.8156066754779223,0.8171013695799173,0.8172725189661585,0.8160181931035159,0.8133051351270633,0.8091763594024171,0.803702336636406,0.7969659107572082,0.789063084956768,0.7801011229581676,0.770195467358449,0.7594667042421407,0.7480379637919653,0.7360328196163942,0.7235736422003007,0.7107803317595318,0.6977693512866238,0.6846529842700091,0.6715387475653732,0.6585288962938562,0.6457199640719021,0.6332022887626739,0.6210594823473976,0.6093678152519723,0.598195503137405,0.587601910791485,0.5776367251091197,0.5683391939602754,0.5597375668569159,0.5518488834101732,0.544679215655816,0.5382243839108565,0.5324710686116808,0.5273981765007746,0.5229783075890666,0.5191791970373594,0.5159650487264172,0.5132977164245827],[0.740355026504342,0.7486144009386747,0.7568062724248822,0.7648621734189867,0.7727057486722625,0.7802526704428968,0.7874107178556757,0.7940800615494856,0.8001537999850489,0.8055187980432186,0.8100568797297322,0.8136464198312685,0.8161643528263671,0.817488643844222,0.8175035388306052,0.8161193670198158,0.8133135144279999,0.8091372951054535,0.8036649200798677,0.7969773893615908,0.7891656332732921,0.7803305059447275,0.7705808730814154,0.7600311457625364,0.748798898189541,0.7370028055359349,0.7247609519247971,0.7121894814522336,0.6994015366667757,0.686506420978934,0.673608922061727,0.660808737464621,0.6481999496090444,0.6358705048076799,0.6239016605985055,0.6123673787808954,0.601333659676645,0.5908578375141249,0.5809878867930549,0.571761820381318,0.563207281841573,0.5553414337451062,0.5481712116761783,0.5416939553617633,0.5358983641752377,0.53076567810238,0.5262709697589498,0.5223844447568915,0.5190726740624623,0.5162997107781896],[0.7416641495289105,0.7498255899934573,0.7579048130580153,0.765833423199869,0.7735354461429766,0.7809272958030001,0.787917905299944,0.7944090597461464,0.8002959716510003,0.8054681413130518,0.809810545009152,0.8132052059120397,0.8155333255181454,0.8166789829082065,0.8165384411094615,0.8150404047152231,0.8121720617945545,0.8079802742711524,0.802538897639061,0.7959292182546401,0.7882392601618796,0.7795647793863502,0.7700085805721362,0.7596788604650268,0.7486872636982876,0.7371470160028473,0.725171286702596,0.7128718182159173,0.700357805188953,0.6877349818896312,0.6751048681355523,0.6625641235583233,0.6502039638541707,0.6381095994947841,0.6263596670445549,0.6150256362406957,0.6041711929166713,0.5938516186212204,0.5841132106923486,0.5749928072692301,0.5665174933437722,0.5587045591032604,0.5515617570392753,0.5450878640456114,0.5392735110141582,0.534102209011549,0.5295514862584557,0.525594053631575,0.5221989320455831,0.5193324952849336],[0.7421952006058766,0.7502218196633171,0.7581518924501381,0.7659174288645177,0.7734432007397751,0.780646756479985,0.7874385970561548,0.7937225477915595,0.7993963640230246,0.8043526160625202,0.8084799242807788,0.811664714615291,0.8137940305077448,0.8147610293869586,0.8144763386151072,0.8128850747190586,0.8099811590891699,0.805805515252842,0.8004268077919845,0.7939249671000048,0.7863861342114916,0.7779023548745158,0.7685713660261274,0.7584956471649643,0.7477810085506805,0.7365350455466237,0.7248656621924723,0.7128797574929675,0.7006820992973471,0.6883743731624874,0.6760543755427421,0.6638153140512615,0.6517451778109435,0.6399261457413887,0.6284340090322592,0.6173375957074377,0.6066981998223575,0.59656903463818,0.5869947460984906,0.5780110366269974,0.5696444551493683,0.5619124033239951,0.5548233891122377,0.5483775304472372,0.5425672812450113,0.5373783275916245,0.5327905890873936,0.5287792598583845,0.5253158326647016,0.5223690633117498],[0.7419879445982838,0.7498464635666007,0.7575946348464415,0.7651651747366992,0.7724839249355914,0.7794699121520537,0.78603556771888,0.7920871429558212,0.7975253666362673,0.8022464170427608,0.8061433513012178,0.8091083186530147,0.8110363051380657,0.8118317957547071,0.8114194693319875,0.8097566486797745,0.806841258454553,0.8027093315228339,0.7974230537119333,0.7910585105265971,0.783699194696233,0.7754339216985389,0.7663561601809572,0.7565633315982623,0.7461557980099616,0.7352356496437064,0.723905448772756,0.7122670373228385,0.7004204608692541,0.6884630223412538,0.6764884551958809,0.6645861940774898,0.6528407173690849,0.6413309380815923,0.6301296257246338,0.6193028512240009,0.6089094587518906,0.5990005813152663,0.5896192292120587,0.5807999893880316,0.5725688764083354,0.5649433700462815,0.5579326602141355,0.5515380996228847,0.5457538428270329,0.5405676323221771,0.5359616817535566,0.5319136040909769,0.528397337458385,0.5253840305107615],[0.7410862150372352,0.7487470524910631,0.7562844032801903,0.7636319685919537,0.7707169610846547,0.7774602128379322,0.7837764484528722,0.7895747672337758,0.7947594001419087,0.7992308537049895,0.8028876504915405,0.8056290588153575,0.8073594589144779,0.8079950494441754,0.8074727125278577,0.8057587086837688,0.8028532908795619,0.7987884910529095,0.7936202342870976,0.7874194063670223,0.7802656280622103,0.7722441336516787,0.7634443807640915,0.753959193238688,0.7438838997523471,0.7333153545736248,0.7223508877562683,0.7110872587028708,0.6996196672228014,0.6880408490375237,0.6764402611721398,0.6649033492764683,0.6535108827273906,0.6423383428221486,0.6314553530981356,0.620925147660571,0.6108040822555865,0.601141202380392,0.5919778913102531,0.5833476265943863,0.5752758744603835,0.5677801465051513,0.5608702322213558,0.5545486061105342,0.548810992399642,0.5436470570028239,0.539041187815543,0.5349733216388541,0.5314197784397197,0.5283540697135987],[0.7395372759560787,0.7469746464335997,0.7542762032639168,0.7613769032174937,0.7682056294696294,0.7746853574985749,0.7807334994311484,0.7862624827207155,0.7911806491705142,0.7953936140553509,0.7988063123810877,0.8013260703923923,0.8028670912800685,0.8033565043843475,0.8027413218059866,0.8009944837732809,0.7981176664940002,0.7941395440644581,0.7891103626288503,0.7830953715116048,0.7761694328278755,0.7684135869598882,0.7599131263020927,0.7507564363556658,0.7410340906623054,0.7308379711356315,0.7202603604606066,0.7093930254371039,0.6983263250795525,0.6871483692326555,0.6759442403029237,0.6647952797955374,0.6537784348568639,0.6429656579789613,0.632423354704523,0.6222118786307667,0.6123850791796517,0.6029899142585755,0.5940661456963683,0.585646138765228,0.5777547869636275,0.5704095788966184,0.563620815821579,0.5573919775079418,0.5517202224987234,0.546596998829306,0.5420087344429867,0.5379375737274508,0.5343621276019888,0.5312582085275553],[0.7373911691478335,0.7445831666537266,0.7516280028678003,0.7584621625062955,0.7650165065907649,0.7712165076337316,0.7769826813054684,0.7822312802382171,0.7868753465236019,0.7908262643161242,0.7939960067681804,0.7963003006264399,0.7976628569460126,0.7980205175701467,0.7973286043002034,0.7955651787702904,0.7927328385013259,0.7888574026859482,0.783984064054824,0.7781724902827989,0.7714923445597922,0.7640199629079312,0.7558361701680248,0.747024860767013,0.7376719685082871,0.727864586583835,0.7176901294339563,0.7072355073963119,0.6965863198934236,0.6858260815674936,0.6750354929457929,0.6642917614482728,0.6536679738599542,0.6432325192225317,0.6330485615820978,0.6231735646714708,0.6136588745997115,0.6045493709778043,0.5958832005430642,0.5876916092062281,0.5799988877142285,0.5728224424343444,0.5661729963835251,0.5600549174524994,0.5544666621629224,0.5494013157027918,0.544847203583379,0.5407885476706531,0.5372061395649133,0.5340780068361942]],[[0.142121482807979,0.13953996802909557,0.1370161108068743,0.1345882302537405,0.1322976646947466,0.13018770389309742,0.128302134563224,0.12668342116978515,0.12537060543657058,0.12439707833787382,0.12378844206758693,0.1235607158777237,0.12371912972361664,0.12425768520262243,0.12515955382090183,0.12639825455682183,0.12793943985043188,0.12974304926074057,0.13176557454433593,0.13396221230977778,0.1362887423957004,0.13870304081277934,0.1411661991952589,0.1436432695059032,0.14610368136964477,0.14852139240453055,0.15087483362940426,0.15314670684377563,0.15532368231707103,0.15739603560905233,0.15935725330810338,0.1612036296310856,0.16293386941751936,0.16454870804044902,0.16605055498120852,0.16744316506122478,0.16873133937518586,0.16992065663200873,0.17101723471911334,0.17202752172931257,0.17295811532540797,0.17381560908842317,0.1746064643462097,0.17533690587284476,0.17601283976316,0.1766397917094568,0.17722286383579872,0.1777667081816281,0.17827551487647864,0.17875301301812457],[0.1385712299070121,0.13569042112148266,0.1328618966310257,0.130129102575025,0.12753966589387242,0.12514425364689064,0.1229949033061383,0.12114281787431483,0.11963570574522403,0.11851485477378158,0.11781224026712163,0.11754804166029502,0.11772894483188623,0.11834751565607282,0.11938275798905353,0.12080176260560192,0.12256217498306099,0.12461510881139201,0.1269081250713614,0.1293879656833301,0.13200283930071402,0.13470416805268234,0.13744779352498607,0.14019469862100106,0.14291133098608552,0.14556962075275476,0.1481467788308776,0.1506249487531915,0.15299076993090824,0.15523489582018576,0.15735149823390893,0.1593377792291033,0.16119350454011983,0.1629205670746712,0.164522585146858,0.16600453751140018,0.167372435562447,0.16863303200597135,0.16979356470199844,0.1708615340466779,0.17184451211045745,0.17274998168651529,0.17358520337880495,0.17435710883816977,0.17507221822088292,0.17573657989182517,0.17635573032817492,0.17693467210833475,0.1774778678069429,0.17798924757266185],[0.1349182803932186,0.13171278558755328,0.1285506416732265,0.12548070102288875,0.12255750691845975,0.1198401508587495,0.1173904191795515,0.11527016438031774,0.1135379517411214,0.11224519945391151,0.11143222031122428,0.11112472392003747,0.11133137548344765,0.11204287971509999,0.11323277949469085,0.1148598139024225,0.11687138908325104,0.11920756969461764,0.12180501973540067,0.12460046392779323,0.12753343015403984,0.13054820594331762,0.1335950638947666,0.13663087686735903,0.13961926507618055,0.14253041023287139,0.14534065088506748,0.148031947986358,0.15059128600712252,0.15301005501860518,0.1552834437289222,0.157409862067974,0.15939040389680742,0.16122835499128177,0.16292874793936538,0.16449796344293455,0.1659433763019474,0.16727304376278027,0.16849543370091144,0.16961919011489912,0.17065293351802888,0.17160509394882809,0.17248377443403531,0.17329664280242024,0.17405084975720728,0.17475297107361526,0.17540897170975836,0.1760241895224703,0.1766033361849363,0.1771505128297779],[0.13119490688706018,0.12763995764332106,0.12411495384367663,0.12067423179305987,0.11737974018403072,0.1143000245363404,0.11150828278468855,0.10907931811633516,0.10708535653812984,0.10559094482183039,0.10464746817673039,0.10428812671438321,0.10452433624240152,0.10534434915028958,0.10671442633447104,0.10858229260419965,0.11088211724546354,0.11354005498556478,0.11647948017236888,0.11962533520622677,0.12290734213382377,0.12626208660574567,0.12963413754464473,0.13297642551283403,0.1362500999070818,0.13942405097245816,0.1424742390424525,0.1453829323703009,0.14813792134555226,0.1507317516757307,0.15316100128168383,0.1554256136459352,0.15752829263381807,0.1594739591057284,0.16126926698582955,0.16292217514355223,0.164441570982042,0.1658369416673891,0.16711808923770302,0.16829488624230668,0.16937706897369192,0.17037406570352193,0.17129485758388777,0.1721478700140544,0.17294089230621237,0.17368102342908864,0.17437464149178145,0.17502739448223012,0.17564420962613314,0.17622931861090918],[0.1274408353835391,0.12351344903951104,0.11959714817410665,0.115751507462227,0.11204608832561615,0.10855976392328273,0.10537888106829596,0.10259389698263426,0.1002942721550739,0.098561745116715,0.09746265577331611,0.09704057438255682,0.09731083909806792,0.09825840709304758,0.09983962510915503,0.10198743935076061,0.10461870573054798,0.10764198472522175,0.11096449757551594,0.11449749963594813,0.1181598863216891,0.12188021988812348,0.1255975319055412,0.12926127582628616,0.13283074794020672,0.13627421542669826,0.13956791527799775,0.14269502834979267,0.14564468997429286,0.14841106980390348,0.15099253527434867,0.1533909020832103,0.15561076891082384,0.15765893051866453,0.15954386216432428,0.16127526819482477,0.16286368821778477,0.16432015507868825,0.16565589978429568,0.16688209937531637,0.1680096644854127,0.1690490638845819,0.17001018367653986,0.17090221900689656,0.17173359616331252,0.17251192284435665,0.17324396418212368,0.17393564186967056,0.1745920535115844,0.17521750912289283],[0.12370356679782724,0.11938410212394197,0.11505044477917079,0.11076668632042896,0.10660971985568779,0.10266922894589713,0.09904631850071192,0.09585012907223936,0.09319184782882735,0.09117594687234853,0.08988934517480093,0.08939034136537975,0.0897000403660915,0.09079886503962066,0.0926293250806831,0.09510413964914681,0.09811724139703377,0.10155487685389988,0.10530479625503697,0.10926268303164913,0.11333589949178288,0.11744510456309322,0.12152441024849378,0.1255206543193851,0.12939221297135245,0.13310763141274876,0.13664423856294378,0.13998683581004465,0.14312650182627606,0.14605952722342233,0.1487864773589673,0.15131137393145708,0.15364098290474526,0.15578419577168523,0.15775149200318364,0.15955447201666348,0.16120545172203563,0.1627171114187495,0.16410219338051757,0.16537324379138368,0.16654239574340385,0.1676211907558318,0.1686204367343359,0.1695501004814317,0.17041923283690316,0.17123592432250886,0.1720072888491522,0.17273947267946527,0.1734376854835803,0.17410625003159702],[0.12003827802866289,0.11531242771167469,0.11053990121496313,0.10578794200278434,0.10113973386951114,0.09669549666624552,0.09257218226448302,0.08890069981939346,0.08581943119336413,0.0834631399661671,0.08194763991230977,0.08135278129203811,0.08170846256963533,0.0829886829323284,0.08511605499644995,0.08797497936727011,0.09142867536756395,0.09533513022235601,0.09955901575071233,0.10397890888682358,0.10849058679683163,0.11300763443854438,0.11746048738955592,0.12179471719312027,0.12596906085161338,0.12995347103104823,0.13372732005372323,0.13727780788373536,0.14059858041736567,0.14368854344593715,0.14655084937224064,0.1491920320533066,0.15162126661676628,0.1538497339398444,0.15589007275417122,0.15775590558046404,0.1594614276791973,0.16102105081930107,0.16244909586630607,0.16375952995273327,0.16496574531368371,0.16608037776210233,0.16711516327001752,0.1680808312601521,0.16898703305871013,0.1698423035899009,0.17065405388875793,0.1714285914551526,0.17217116494688656,0.17288602927933228],[0.11650708980441954,0.11136829774990037,0.10614277364673616,0.1008987643863142,0.0957236364535005,0.09072660250061489,0.08604035040451334,0.0818200471785311,0.07823747159593117,0.07546784735076105,0.07366840292405002,0.07295163840140069,0.07336146450170841,0.07486244543132521,0.07734753102757962,0.08066045289679756,0.08462287352390618,0.08905732467279263,0.09380198735871362,0.09871775718278214,0.10368993212518114,0.1086268869468157,0.11345741374922719,0.11812770714031504,0.12259847930189485,0.1268424014634855,0.13084191941299433,0.13458742297862014,0.1380757240797897,0.14130879280659836,0.1442927044928873,0.14703675729666008,0.14955272688044646,0.15185423138517526,0.15395618568985084,0.15587432890258426,0.15762481318733715,0.15922384546151536,0.16068737625741483,0.1620308321664387,0.16326888981292376,0.16441529027109095,0.1654826932923939,0.16648257071692876,0.16742513808592552,0.1683193228530426,0.16917276682034077,0.16999185961140006,0.1707817992412626,0.1715466752352788],[0.11317745884370346,0.10762964671366465,0.10194785673821034,0.09619837534132133,0.09046932603237386,0.0848754974735457,0.07956296485210339,0.07471172503715326,0.07053288776136885,0.06725524582452796,0.06509650092828027,0.06422063362798813,0.0646951149471387,0.06647000644748789,0.06939204949638311,0.07324493252691126,0.07779385395392913,0.08281795099608091,0.08812680173201977,0.09356501426590542,0.09901032570770821,0.10436911465637705,0.10957143821606177,0.11456650340881176,0.11931885220797683,0.12380526166474073,0.12801226182413913,0.13193415436257988,0.13557142503673433,0.13892946154697206,0.1420175068854585,0.1448477940153295,0.14743482045136092,0.1497947313865898,0.15194478798469044,0.15390290381558425,0.1556872375069135,0.1573158337530963,0.15880630801206772,0.16017557261330895,0.16143960365453186,0.1626132490269808,0.16371007824046435,0.16474227450077508,0.1657205688317282,0.16665421506194922,0.1675510033569084,0.16841730881495245,0.1692581705951279,0.1700773962122947],[0.11011946523552446,0.10417979277865175,0.09805321036352777,0.09180045824810366,0.08550566483191592,0.07928342511621539,0.0732873167933164,0.06771853379766742,0.06283053109664685,0.058920734653376966,0.05629611528786704,0.05520554606775968,0.05575883354629352,0.057882409070762024,0.061347054334105054,0.06584531470723119,0.07106637290766694,0.07673917290188013,0.0826460410372979,0.08862010307187491,0.09453692802668989,0.10030561071902153,0.10586115090642739,0.1111584617808958,0.11616780851413162,0.12087136379240215,0.12526059609293885,0.12933426813844168,0.13309688082162896,0.13655744314944945,0.1397284818861068,0.14262522831359842,0.1452649365884947,0.147666300653467,0.14984894602977064,0.15183298003728415,0.1536385896623678,0.15528568077202426,0.15679355584541746,0.15818062995516205,0.1594641864299551,0.1606601745081374,0.16178305140813748,0.16284567069017705,0.16385921769712852,0.16483319140842034,0.16577543040798914,0.166692179046599,0.1675881884438912,0.16846684586412417],[0.10740185916685614,0.10110304219248867,0.09456162303991138,0.08782912397268183,0.08098010198763539,0.07412095165339459,0.06740233504199097,0.0610356775914273,0.05531130700773667,0.05060718694370652,0.04736068802503157,0.04596737986859168,0.046619742677266436,0.04920265308147515,0.05335354256058624,0.058623526172747666,0.06460352777517751,0.0709715467151179,0.07749103461942604,0.08399340529491056,0.0903601940971751,0.09650912970723027,0.10238416403288779,0.1079485103428945,0.11317977041236567,0.11806647194554076,0.12260555618523135,0.1268005119573539,0.1306599556265673,0.13419652283460765,0.1374259805902804,0.140366496199154,0.14303801833285512,0.14546173873685111,0.14765961277018272,0.14965392440194475,0.15146688715810436,0.15312027718439217,0.1546350982307119,0.1560312810228897,0.15732742117575843,0.15854056052674886,0.15968601657660647,0.16077726371498025,0.16182586824663495,0.16284147713536026,0.1638318580965449,0.16480298644980196,0.1657591722185474,0.16670321951113146],[0.10508693755953816,0.09847846461563314,0.09157332928052343,0.08441097650518216,0.07705122926375343,0.06958341903335462,0.06214099683724943,0.05492501540341876,0.048239968460264654,0.04253804641893986,0.03843452916819576,0.03658842694912574,0.03737152118772198,0.04058776111315184,0.04562124044182122,0.0518036628197428,0.05861354897684078,0.06569336855911913,0.07280733687950625,0.07980038605887914,0.08657002389392163,0.09304867764760685,0.09919273307787392,0.10497559072066426,0.11038312129861183,0.11541058067637047,0.12006043776435324,0.12434079065836229,0.12826417203430804,0.13184661737777992,0.13510691273655745,0.13806596534491114,0.14074625784963896,0.14317135894586672,0.14536547220939067,0.14735301198758735,0.14915820099136565,0.15080468897788593,0.15231519568838742,0.15371118396461245,0.15501257063677376,0.1562374833059561,0.15740207055021127,0.15852037147297235,0.15960424808769194,0.16066338107871556,0.1617053263305652,0.16273562661870714,0.16375797030952882,0.16477438705480207],[0.10322464325839834,0.09637217629020355,0.08917605556216843,0.08166266155953751,0.07387419358737955,0.06587622573873456,0.05777095598734357,0.04972188295802731,0.04200161417552243,0.03508217395754538,0.029767624197222987,0.027187947837327423,0.028157574448957782,0.032299474821411746,0.03847214242396135,0.045691208292593356,0.05335043656993327,0.061102511675766476,0.06874414869758454,0.07615157797970816,0.08324733218262295,0.08998280084133406,0.09632856663629188,0.10226870871088611,0.10779723095314318,0.11291569173710078,0.11763154952405289,0.12195695503527575,0.12590783188953591,0.12950314728504556,0.13276430802876274,0.13571463754946486,0.13837890285355164,0.14078286999490516,0.14295287423874717,0.14491539754563298,0.14669665163433018,0.14832216976001067,0.14981641435823126,0.1512024106673059,0.15250141815686508,0.1537326519205497,0.1549130651063579,0.15605720107079482,0.15717712051206315,0.15828240474747932,0.15938023201154167,0.160475519634402,0.16157112162873566,0.16266806886477864],[0.10184665423993035,0.0948290949405214,0.08743346925171736,0.0796747313841136,0.07157857429520523,0.06318607397502098,0.05456212766358386,0.04581267025504727,0.03712436644108946,0.02886745112377654,0.021875896274856477,0.01798072452860338,0.019252491231641085,0.024830255911109076,0.03240488073102199,0.040679981368982855,0.04909715092060544,0.05739532589777933,0.06543594473686036,0.07313836935459278,0.08045356935041757,0.08735201124287327,0.09381739429702717,0.09984305161327856,0.10542968824779386,0.11058385157195176,0.1153168342945502,0.11964384833656477,0.12358337388771559,0.12715662184411952,0.13038706663543226,0.13330001812666664,0.1359222096239264,0.1382813858767535,0.1404058812246023,0.14232418401861163,0.1440644891800141,0.14565424604575064,0.14711971318487532,0.148485535273253,0.14977435903315425,0.15100650541803703,0.15219971355622214,0.1533689685789967,0.15452642069166891,0.155681397232646,0.15684050365218893,0.1580078039879632,0.15918506708561025,0.16037206190049774],[0.10096151643121627,0.09386572091324971,0.0863742799636103,0.07849489823083584,0.07024229005723326,0.061640218731173375,0.05272483481819183,0.043551200906742776,0.03420908733218542,0.024872239464119525,0.01600996868302345,0.009639205660303986,0.011472251086322511,0.019187911206102054,0.028130855160869984,0.0372072760167878,0.04611613124422841,0.05472950362570709,0.06297728588199308,0.07081639918347563,0.07821980730334833,0.08517157197492713,0.0916641648651139,0.09769677979491392,0.10327416191568799,0.1084057413712625,0.11310496385856526,0.11738875441821167,0.12127707062489991,0.12479251134830392,0.12795995334710722,0.13080619275326177,0.13335957318512642,0.13564958731335613,0.1377064443526982,0.13956060209603846,0.14124226849233748,0.1427808839905698,0.14420460139959124,0.14553978425893907,0.1468105471133474,0.14803836120298794,0.14924174673129859,0.1504360681801369,0.15163344257476763,0.15284276291481372,0.1540698311090521,0.1553175876208637,0.15658641943581234,0.1578745244165942],[0.10055189601284834,0.09346570661716569,0.08598493554853733,0.07811564426512818,0.06986984858179598,0.06126680663807822,0.05233480486102352,0.04311410817451054,0.03366329763081446,0.024078407565282456,0.014583413590548724,0.006426758155933287,0.008291768635069892,0.017050536286443426,0.026380781923095356,0.03560651200633133,0.04456466891663208,0.05317746861820451,0.06139681865200913,0.06919067216823979,0.07653799734401501,0.0834262633346323,0.08984988497234113,0.0958091298613142,0.10130929810120251,0.10636008636097716,0.11097508455171104,0.11517136721229085,0.11896914743565548,0.12239146421204701,0.1254638766836526,0.12821414195174188,0.1306718571742273,0.13286805189969636,0.1348347228959566,0.13660431098049344,0.13820912720045914,0.13968074359701935,0.14104937099525533,0.14234325193849146,0.14358810018767143,0.14480661845042214,0.14601812284848903,0.1472382962082625,0.14847908321870532,0.14974872994207353,0.15105195944346753,0.15239026578804366,0.15376230145055508,0.15516432896179813],[0.1005746835504139,0.09357952591262525,0.08620835777679686,0.07847094557655344,0.07038461212069375,0.06197676718135213,0.05328922965382657,0.04438682802147626,0.03537782170327614,0.026473276670050328,0.018204450536628048,0.012330994676087049,0.01286464129548623,0.019170396462066242,0.027336173481120534,0.03589985341873342,0.04441235642052682,0.05269068774646233,0.060640845725535505,0.06820769970045903,0.07535718542448189,0.08206864146990357,0.08833094752529268,0.09414032220918449,0.09949894905838648,0.10441406485806237,0.10889732702200677,0.11296435432113365,0.11663437086544211,0.11992990125694206,0.12287647543368815,0.12550230946727733,0.1278379356245352,0.12991576244281042,0.13176955391607167,0.13343382627935446,0.1349431710953295,0.13633152381341965,0.1376314067694139,0.13887318354360018,0.14008436644037392,0.14128901951733064,0.14250729547810342,0.14375513596669046,0.145044152287791,0.14638168895715584,0.14777105778911706,0.14921191746860504,0.1507007643147555,0.15223149508851802],[0.10096404590032297,0.0941285071977515,0.08694939143765074,0.07944381650681044,0.07163951553713899,0.06357940589547963,0.05532968016109595,0.04699561135914548,0.038755680741463766,0.03094200132399988,0.024232991510950756,0.0199844557641958,0.01990095341568842,0.023941090969241085,0.03034304905395624,0.037731303747437,0.045425663352772754,0.05309800176300571,0.06057540498938094,0.06775839206551623,0.07458633602585246,0.08102155881565082,0.08704132217694953,0.0926334579978682,0.09779382631069371,0.10252476405691018,0.10683410321583516,0.11073452543739261,0.11424311125077524,0.11738098878574563,0.12017301325810005,0.12264742517627121,0.12483544773677205,0.12677079504997157,0.12848907423675573,0.13002707682755651,0.13142196840022383,0.13271039950360922,0.13392757450082957,0.13510632638799341,0.13627625300846558,0.13746297166643962,0.13868754389126367,0.1399661100586375,0.14130975607253987,0.14272461382469415,0.1442121767814436,0.14576979483237268,0.14739130074803886,0.14906771532126828],[0.10163683580317569,0.09501230080581441,0.08808545334172005,0.08088211504426053,0.07344172868918468,0.06582343349572331,0.0581163503874599,0.05045795875620846,0.04306815770350818,0.036311499716637184,0.03079241552080987,0.02739926905671322,0.02697997711064536,0.029596215648235148,0.03443233838652263,0.04053592619072194,0.04723921313485549,0.05414179295763794,0.06100717170541253,0.06769130437390952,0.07410331439689154,0.08018458099245304,0.08589733634190537,0.09121820926434454,0.09613443711022963,0.1006415805738898,0.10474211633492433,0.10844455112555543,0.11176283936845634,0.11471596121739272,0.11732756046125725,0.11962556815722586,0.12164175635058867,0.12341118147695132,0.1249714917917133,0.12636208902638235,0.12762315206432448,0.12879454940948537,0.12991468620586433,0.13101934822616612,0.13214061667690896,0.13330593103860336,0.13453737058486753,0.13585120853928936,0.13725776798915718,0.13876157952295637,0.14036181195613573,0.14205292411298123,0.14382547074353433,0.14566699055255594],[0.10249931001113785,0.09611807424363192,0.08947947816782921,0.08261739286932272,0.07558123397869951,0.06844243982610496,0.06130467054380795,0.05432010786444111,0.047714954837429074,0.04182497038385223,0.037126541740713025,0.03420269483090988,0.033541323671035156,0.03521981552826788,0.03883080892302947,0.04375949721456409,0.04945817341001851,0.055531330138985625,0.061714161980113695,0.06783180021956954,0.07376764523750681,0.07944293317495296,0.08480422072299096,0.08981578207049279,0.09445496540393537,0.09870933863031382,0.10257492775772975,0.10605512271194492,0.10915997968509612,0.11190573821305445,0.11431442421462877,0.11641344347743485,0.11823509294031467,0.11981593539025975,0.12119600067830998,0.12241779578075435,0.1235251283161375,0.12456177341969864,0.1255700404918005,0.12658932093666192,0.1276547160396012,0.12879585086213902,0.13003597203134368,0.13139140389440712,0.13287140160929514,0.13447839748329687,0.13620859607412894,0.1380528415381087,0.13999766225409707,0.14202639416994847],[0.1034540186671911,0.09732964874805991,0.0909922544014252,0.08448186518667401,0.07785458186152582,0.07118851431419013,0.06459239457748239,0.05821780931614976,0.05227523398625081,0.04705038820428058,0.04290693831762694,0.040243853046470164,0.039376163381217626,0.04038043262206671,0.04304191743838716,0.04696483352707157,0.05173044384504637,0.056988144885983874,0.06247477679965347,0.06800139508123004,0.07343394372248635,0.07867718890155338,0.08366333794126694,0.08834447120704539,0.09268765314129969,0.09667182798491475,0.1002858762630823,0.10352740998603352,0.10640201871375177,0.10892276437304182,0.11110977704572042,0.11298983896450124,0.11459586797363383,0.11596623072504567,0.11714383449227357,0.11817496825454618,0.11910789096773441,0.11999119824660812,0.12087203611448732,0.12179426726062285,0.12279672417677912,0.1239116965531962,0.125163791058786,0.12656926829125034,0.12813590865854352,0.12986339635105146,0.13174415134399067,0.13376449525493372,0.1359060148484393,0.13814698778917311],[0.1044059624429833,0.09853527389641897,0.09249226197426913,0.08632079272714446,0.08008013512592478,0.07384986217163249,0.06773639598085232,0.061881267847872456,0.05647009224199508,0.05173838333585746,0.04796472931605844,0.04543595026618181,0.04437496967785325,0.0448553456172564,0.04676292830908051,0.049840110533781734,0.05377471164442878,0.05827217744835067,0.06308826251446226,0.06803316321338423,0.07296353082341481,0.07777215401401699,0.08237910329806536,0.0867251542121069,0.09076724184938215,0.09447545799908205,0.09783113601774447,0.10082566435572188,0.10345975910732216,0.10574299357047162,0.10769342962089758,0.10933722684299287,0.1107081264316844,0.11184672330825536,0.11279945690307765,0.11361727354764417,0.11435394535484429,0.11506407371733161,0.11580085836344974,0.11661376866159721,0.11754630112754745,0.1186340318966131,0.11990316335288619,0.12136971576382236,0.12303943442904222,0.12490838776462512,0.12696414411220142,0.12918735414342492,0.13155354147006365,0.13403491516676372],[0.10526750065798943,0.09963342526043126,0.09386237152338558,0.08799987329785497,0.08210541380188169,0.07625618503881845,0.07055173357779446,0.06511919277204971,0.06011790283003976,0.05574037980425861,0.05220381743180429,0.0497245382155862,0.04847256313348843,0.048519421141053606,0.049808949788101894,0.05217294352553153,0.05538070422645898,0.05919105407163989,0.06338562072792192,0.06778178514523134,0.07223302030976768,0.07662402939312161,0.08086493031548496,0.08488624285872677,0.08863512547436227,0.09207277299385125,0.09517272560947615,0.097919828504245,0.10030961712915115,0.10234794423191036,0.10405069762415656,0.10544347987810948,0.10656113483698651,0.1074470153979546,0.10815189831497442,0.10873247155559211,0.10924935477046613,0.10976466839376196,0.11033924143488814,0.11102963362394201,0.11188522625444046,0.1129456833178457,0.1142390774659427,0.11578090377927203,0.11757407890338151,0.1196098744784588,0.12186960141410261,0.124326777830832,0.1269494918797354,0.12970270390933958],[0.10596186415348091,0.10053659282933773,0.0950036703339158,0.08940859332621015,0.08380896842664136,0.07827724943875695,0.07290390358961833,0.0678006333765455,0.06310264474409358,0.05896784568419065,0.055569461502276526,0.05307802660646239,0.05163161293560232,0.05130129977746598,0.05206777450132657,0.05382342085407302,0.05639901264865447,0.0595995359447369,0.06323338559864634,0.06712883604978813,0.0711398240151904,0.07514559974490104,0.07904791790839841,0.08276783558003749,0.08624299889609202,0.0894256534213024,0.09228132767362215,0.09478804188259626,0.09693587858443783,0.09872676375695803,0.10017432244578015,0.10130368209369216,0.10215109864200413,0.10276327796925673,0.10319626478627203,0.10351378210655707,0.10378493820585573,0.10408128503564722,0.10447331654619078,0.10502662816109296,0.10579809212702947,0.10683249413143599,0.10816007942433767,0.10979534822685119,0.11173723743107676,0.11397058548941356,0.11646857314015296,0.11919571985181474,0.12211101043174663,0.12517080527055383],[0.10642538571663035,0.10117337276970438,0.09583709611425613,0.09046087125922897,0.08509919411738257,0.0798186550688954,0.07470005519155955,0.06984041284680138,0.0653541281923557,0.06137190183431553,0.05803522327789565,0.05548399504375262,0.05383642655408008,0.05316471063456828,0.053475400673907596,0.05470441769347338,0.05672972683641173,0.05939495438112104,0.06253330521907223,0.06598475047057682,0.0696051893826591,0.07326966343679839,0.07687230822544833,0.08032501810874092,0.08355591782283539,0.08650811104039989,0.08913883149308126,0.09141896471622606,0.09333284996559037,0.09487825584630821,0.09606641907719325,0.09692202916663403,0.0974830275631543,0.09780006914699747,0.0979354732425858,0.09796148310466143,0.09795767550306345,0.09800743705802291,0.09819356719783418,0.09859327453021512,0.09927306404829181,0.10028418911615186,0.10165937344145642,0.10341133933588816,0.10553333682063569,0.10800146538229523,0.11077825853255355,0.1138168578777818,0.11706514832559688,0.12046939716131363],[0.10660869152961328,0.10148929898759064,0.09630361190345949,0.09109415387913236,0.08591179105506419,0.08081701530518254,0.0758813491251418,0.07118866716731168,0.06683595744968775,0.06293261483474095,0.05959684279812765,0.056947475034794436,0.05509023119399668,0.0540998146334811,0.05400285317892428,0.05476876189939992,0.056313114627742675,0.05851190955862739,0.06122024394930683,0.0642888879472954,0.06757558259728816,0.07095114055484933,0.07430193076307491,0.07753039997267289,0.08055478515066337,0.08330865377133632,0.08574055539171184,0.08781387204630109,0.08950686081855538,0.0908128391291784,0.09174043893582694,0.09231383160702981,0.09257279157632324,0.09257242162713471,0.09238231051641266,0.09208484918895166,0.09177242287897602,0.09154326365213422,0.09149593384083089,0.09172273139757953,0.09230271341582502,0.09329538506676974,0.09473620727585338,0.09663480506465445,0.09897615335695858,0.10172431172227445,0.10482776465704823,0.10822526933793877,0.11185129097641779,0.1156404578726062],[0.10647712842436054,0.1014468335318631,0.09636352788074301,0.09126778351089075,0.08620686322499249,0.08123552047553685,0.0764169189741075,0.07182357970984617,0.06753809034741627,0.06365301580937593,0.06026904378966532,0.057490048536155906,0.05541388624743252,0.05411895132924049,0.0536489967088268,0.05400123478660449,0.05512285446628845,0.0569176457438064,0.05925969354802398,0.062008766746248146,0.06502315273541502,0.06816833261457415,0.07132191813019848,0.07437604291383228,0.07723833367558698,0.07983223514579585,0.08209713168036976,0.0839884855440558,0.08547808365589689,0.08655441383091307,0.08722314606997877,0.08750765197343327,0.08744944131811021,0.08710832046743645,0.08656198107721011,0.08590462155839962,0.0852441242311778,0.08469732820612697,0.0843831492509467,0.08441378185845773,0.08488494022962728,0.08586681230647622,0.08739770118736388,0.08948187641187426,0.09209202043103955,0.09517535810744113,0.0986617290456658,0.10247179005450434,0.10652404271946686,0.110740076003516],[0.1060106743270156,0.1010248535000437,0.09599540205341138,0.09096113859302991,0.08596614782519026,0.08106019096512476,0.07629926451674153,0.07174632087537017,0.06747206250701689,0.06355550891813742,0.060083683405681654,0.05714932744398294,0.05484527380663291,0.0532545123663605,0.052436605006445286,0.052413719840592315,0.05316144776711148,0.05460852452986313,0.05664558951240692,0.05913914849563823,0.06194583447558847,0.06492374310961326,0.06793996700373853,0.07087494389439365,0.07362468397944995,0.07610180850955653,0.07823603733256976,0.07997450736198151,0.08128213221911959,0.08214210842233692,0.08255660550859076,0.08254761963209852,0.0821579002482657,0.0814517578549632,0.08051541164862563,0.07945633668899037,0.07840085362078703,0.07748907347475478,0.07686646367660206,0.07667198175645881,0.07702401393749703,0.07800687236952027,0.07966142052950557,0.08198261374455994,0.08492444436949416,0.0884102581363448,0.09234511221874511,0.09662718669834186,0.10115654940877195,0.10584087578854906],[0.10520352620870094,0.10021787693625174,0.09519479751545962,0.0901718240528562,0.08519057816699069,0.08029683357773326,0.07554075707956291,0.07097743342401497,0.06666774174347895,0.06267950532408925,0.05908852447391084,0.05597859546003344,0.05343902956745874,0.05155792753629039,0.050410276472289184,0.0500423693166927,0.05045728748861092,0.05160759237101314,0.05339872353778635,0.05570136958695126,0.058367471921640886,0.0612447673682821,0.06418735699944027,0.06706219259695154,0.06975252071202977,0.07215947333115573,0.07420272207133641,0.07582078949734578,0.07697136867613305,0.07763184967322732,0.07780015982371234,0.07749595909990271,0.07676216015793887,0.07566662988691782,0.0743037347630575,0.07279507527702156,0.07128830664792915,0.06995246837474975,0.06896808508956816,0.06851107749968978,0.06873179218714287,0.06973379033335511,0.07155929139084947,0.07418675556110937,0.07754101487672949,0.08151114814666956,0.0859695148123622,0.09078719016579738,0.0958440892657614,0.10103427687501883],[0.10406350103373459,0.0990351846726287,0.09397305839901793,0.08891404683834804,0.08389823768435377,0.0789686145164295,0.07417096260158727,0.06955414217160219,0.06517094220591545,0.06107965299510536,0.057346238496986966,0.05404645275296914,0.05126641068038621,0.04909925357594336,0.047635441009077996,0.04694607624685155,0.04706293326779538,0.047963099815530125,0.04956584665506579,0.051743142526067966,0.05433821229594782,0.0571844525650102,0.06011984484265594,0.06299583391348128,0.06568184640631615,0.06806712315179783,0.07006121369090523,0.0715940039893712,0.07261578254412032,0.07309762971930135,0.07303230014103711,0.07243570962320597,0.07134909179682249,0.06984180570677725,0.06801458229672201,0.06600258589857133,0.06397690521931539,0.062141942741248526,0.060725044320662426,0.05995493941412926,0.060029251485048,0.06107894087883943,0.06314413512313884,0.06617316721546077,0.07004412130351263,0.07459672022348704,0.07966129182468783,0.08507816701040515,0.0907074491841886,0.09643203904102281],[0.10261132933089806,0.09749992487557671,0.09235618576105593,0.0872172306380483,0.08212270101774787,0.07711415162072327,0.07223456481194886,0.06752825253620613,0.06304149586051284,0.058824287355335986,0.05493337514619865,0.051436300976271054,0.04841512295758423,0.04596705669571585,0.04419802297313201,0.043205803535519643,0.04305425531115973,0.0437478184978124,0.0452194936917715,0.04733897144635545,0.04993532338233623,0.05282240901795192,0.055818409260435846,0.05875731459046514,0.06149412496207734,0.06390636965365351,0.0658939571194405,0.06737856115967503,0.06830318101946407,0.068632205045349,0.06835217752325728,0.06747343943722477,0.06603283120684013,0.06409765699092691,0.06177102935128719,0.05919835733429506,0.05657375222436885,0.054142982991549585,0.05219616596947019,0.05104062545879882,0.05094866888039233,0.052092777522940906,0.05450173386872459,0.05806635015998929,0.06258794488174492,0.06783630896223014,0.07359124177851897,0.07966254614453357,0.08589503270425052,0.09216614897805245],[0.1008798697831222,0.0956482288070562,0.0903838358725587,0.0851248758170016,0.07991173713585416,0.07478605326572152,0.0697897558624533,0.06496444535172739,0.060351548270053255,0.055993863797218775,0.05193908200319735,0.0482454727232811,0.044988899065738906,0.04226834044329678,0.04020447659135292,0.03892448122659551,0.038530209752491884,0.0390590512182685,0.04045858638120883,0.04259131415808001,0.045264498659496374,0.04826577597577283,0.051389585936930424,0.05445114236575051,0.0572913932230371,0.05977731231317482,0.06180046152474624,0.06327534638267575,0.06413823504726297,0.06434672029612762,0.06388018406894495,0.0627413504806596,0.06095922769989948,0.058593916377839506,0.05574396129849038,0.052556982988342146,0.049243710034056,0.04609281566690286,0.043476542693999545,0.041824326385760176,0.04153744406747252,0.042857335934191075,0.045775583586409894,0.05006675028750611,0.055405183843034674,0.06146811385847415,0.06798412318806869,0.07474178067618466,0.08158177141129745,0.08838565134527172],[0.0989132252802664,0.09352831336531557,0.08810841256525001,0.0826936330526894,0.07732633937271557,0.07204986259279596,0.06690704159486793,0.06193889601556794,0.057183978432330744,0.05267923294969608,0.048463385209805164,0.044583760405896226,0.04110654432705015,0.03812824465141061,0.035781968509348776,0.03422728411627606,0.03361310168217331,0.034019334481430456,0.035409985874421124,0.037632641425008585,0.04046153980178906,0.043649796920965746,0.04696470926947258,0.05020298365614497,0.05319358424332666,0.05579545750254557,0.05789410775975739,0.05939862855832187,0.06023966562510681,0.060368389326900154,0.05975649720946385,0.058397367912784624,0.056308697789461216,0.05353730264727263,0.050167348821578396,0.0463341947429052,0.04224713612533813,0.038224072278798676,0.03473245832399771,0.03239611385357637,0.03186703770521407,0.03351810532970005,0.037223108328617804,0.04250726991999869,0.04884575237151282,0.055817706476426344,0.0631227090681417,0.07055248016536161,0.07796194543269923,0.0852487604377719],[0.096765695253951,0.09119949249606434,0.08559417000643621,0.0799925125751819,0.07444002389083076,0.06898338116378645,0.0636684734493604,0.05853825769751243,0.05363097833391293,0.048979737514960105,0.04461489281800083,0.040571054574638055,0.036900046993908565,0.03368913041675145,0.031078471283651318,0.0292621846005233,0.02844931660674125,0.028778045101169124,0.030231391608529064,0.03262848428069606,0.03569381949291794,0.03913682029046707,0.042696647519761995,0.046154858721557876,0.04933292726282702,0.0520858540524344,0.05429630403626057,0.0558703313292937,0.05673462228195438,0.05683496993007879,0.05613577640287703,0.05462055581958153,0.05229365668160666,0.04918382219853948,0.04535097755231568,0.040899284197635055,0.03600318184878881,0.030960878819623682,0.02630002214920551,0.022928964168197195,0.022063022865262058,0.024384901279133498,0.02935272015532741,0.03595008349505728,0.043417485817736814,0.05130195089955211,0.059335188193155,0.06734924201126428,0.07523279012265131,0.08290903406081204],[0.09450045838977994,0.08873096421265322,0.08291617482844692,0.077102079469628,0.07133827779368072,0.06567631847023042,0.060167346746255596,0.054859145397193707,0.049792986409399095,0.04500128989414393,0.040507914747283616,0.036333806014712214,0.0325111909210182,0.029108432128920593,0.02626242671563348,0.02420078389985818,0.023210755069954868,0.023514597642536404,0.025116316280738633,0.027781021512747486,0.031159586229600782,0.03491109353961089,0.038751573057754105,0.04245555409169633,0.04584413265298902,0.048773571194802516,0.051127320577508684,0.052810995903957304,0.05374936894523152,0.05388466716154714,0.05317575649927901,0.05159801634050894,0.04914391686744196,0.04582456398772848,0.041672963959028586,0.036750967905647566,0.03116538301700553,0.02511061083150347,0.019000681637091305,0.01391865524558878,0.012471533329755508,0.016333253712029587,0.02323280910357457,0.031289129502659906,0.03977624434706446,0.04838509420820961,0.056950579449461886,0.0653687566797243,0.07356784471448001,0.08149616443451922],[0.09218785294829578,0.08620019020472942,0.08015889930965127,0.07411338170764425,0.06811791918930417,0.06223010598756064,0.05650834930610226,0.05100829900089281,0.045778335216227276,0.04085486235706568,0.03625928514002841,0.03200018114969979,0.028085961520810672,0.0245542222235538,0.02152131365144531,0.019239611755815463,0.018097851345958312,0.01844500351151707,0.020301868993103368,0.02333040141556088,0.02708000356136258,0.031164542701859435,0.03529253715877724,0.039244587852331744,0.042849768062234034,0.0459704973378865,0.04849399313490124,0.05032759705453773,0.05139622410792779,0.05164097121533957,0.051018388042903956,0.04950017009332572,0.04707318085793384,0.043739817278524495,0.03951887240398688,0.0344473718448855,0.028584892383266818,0.022026092466523244,0.014950995831641709,0.007969002471487463,0.005682765510135762,0.012266212950827445,0.02074473669337733,0.02960425384554857,0.038552030898242585,0.0474529575626112,0.056217495215009274,0.06477863704841301,0.07308451266575133,0.08109503334972039],[0.08990312580401229,0.08369066160614064,0.07741415110572601,0.07112623441220901,0.06488594723935645,0.058757487915010856,0.052807929499140295,0.047103489388303,0.041704058920082956,0.03665616001304212,0.031985706497844435,0.027694280687800835,0.02376609571396837,0.020196718895208125,0.017057504010721373,0.014602312993945963,0.013346786900271957,0.013835596734126416,0.016076856355963256,0.019543442249844212,0.02367354143996909,0.02806764964598688,0.03245314492173983,0.036630471458849644,0.04044262387379784,0.0437605423683729,0.04647634248383071,0.04850015949602127,0.049758670234991746,0.05019444092697404,0.04976575417792461,0.04844682182344753,0.046228460991537684,0.04311951822682316,0.039149751649552124,0.03437600590136863,0.028897001053705077,0.022894753957053517,0.016775828971859176,0.011734652504022858,0.010950923907839829,0.015765215195397798,0.023152771566713047,0.03141917309100279,0.03999707521713266,0.04864212267080604,0.057216787061584375,0.06563013249971403,0.07381705809021878,0.0817295353970611],[0.08772357840214828,0.08128888265400476,0.07477803752115612,0.06824639415426476,0.0617572500470083,0.055381150803444225,0.04919419690952696,0.04327479014976971,0.03769808494578394,0.032527465919292335,0.027803193677944905,0.023530908005394438,0.019677924021233358,0.016193171644561948,0.013077075250770384,0.010542335870902388,0.009247362473122297,0.010026743624448685,0.012769088324106932,0.016664141226221084,0.02110111414140323,0.025725602582076672,0.03030662371907245,0.034669611987557664,0.038670877903417014,0.04218820901947558,0.045117442332079274,0.047371291295522915,0.048879087070520195,0.04958699377537959,0.049458638370645666,0.04847631640515881,0.04664316879485007,0.04398713271049196,0.040568339611854756,0.03649363573296235,0.03194663885279821,0.027252294716380545,0.023009027622641506,0.020265916584014953,0.02031456344322705,0.02356679083515648,0.02918045368179954,0.03614115911316161,0.04379402447871089,0.05176413782184113,0.0598278096780336,0.06784157955457373,0.0757078153078674,0.08335759269769408],[0.08572516638718776,0.07908054427397422,0.07234678595093519,0.06558120944037747,0.05885043434589385,0.05223029249129204,0.04580498104824148,0.039664883191751314,0.033902096175574055,0.028602220508721948,0.023830783890753934,0.019614191346221502,0.01592118818706148,0.012664232286440242,0.009760780531022095,0.007335583360637856,0.006173993325136248,0.007424885956821857,0.010638731450833014,0.01480134946918776,0.01939314600242244,0.024139354320595875,0.02884723225687946,0.033358217575080576,0.037534748310397055,0.04125686662110678,0.04442165103048604,0.04694347911170822,0.04875459751010181,0.049805966943432485,0.05006855902202896,0.04953544209902061,0.048225216750895035,0.04618774873756457,0.043513827793466346,0.0403514647084533,0.03693269227514354,0.03361324783366712,0.030912571478831374,0.029491911583994147,0.029956398580420443,0.032525060030367384,0.03693189638693348,0.042677471162501215,0.04928836073077766,0.056405803339632105,0.063776622794009,0.07122365212776101,0.07862136476619982,0.08587957559829441],[0.08397880487907655,0.0771461208619034,0.0702115631141019,0.06323367301630319,0.05628129320627692,0.04943399853685514,0.04278208098662261,0.036425681582729845,0.030472260580208632,0.025030800972936456,0.020199800057450142,0.016044922196738382,0.012565414196368868,0.009666886138719093,0.007200435141757764,0.005197861851334021,0.004499923834749182,0.006233309456587721,0.009629440340910976,0.013819038315119107,0.018421582600515102,0.02321029075250763,0.028004946104173603,0.032648106675852745,0.037000372599980694,0.040940020877396316,0.04436356095612295,0.04718644585423307,0.04934388144440248,0.050791889113068624,0.05150887202615832,0.05149802528983545,0.05079105570124685,0.04945384321695611,0.04759482141074787,0.045376710025523695,0.04303098332316812,0.040870225010682125,0.039283941739000156,0.03869205783863252,0.039440480721251295,0.04168150694383896,0.045333174447798455,0.050149965716923026,0.055832284218899034,0.06210120868579734,0.06872687956518894,0.07553007017812254,0.0823742690535388,0.08915652356057402],[0.08254684402182394,0.07555645967335445,0.06845294042878754,0.061295506918230006,0.0541543063364319,0.0471111693553806,0.04026016365146605,0.03370776022339265,0.027572213250072086,0.02198117288961771,0.017064978241771674,0.01293930619867005,0.00966542993182446,0.007186540408165528,0.0053178822318662574,0.004012621752664279,0.003992329602776862,0.005964702284672229,0.009297276559017726,0.013406339069250903,0.017983090608514888,0.022808186115922915,0.027696247627498612,0.03248376564129612,0.037026951808501775,0.04120177727542435,0.04490442560264548,0.04805183246874209,0.05058235941409178,0.052456756809559794,0.05365961402629083,0.05420152371369852,0.05412220241118304,0.053494771128115445,0.05243119808909802,0.051088308592429826,0.049672382259127755,0.04843783761092512,0.04767249909931329,0.04766199539993842,0.04863520408601588,0.05071120053183523,0.05387779897438684,0.0580136510074755,0.0629357932227536,0.0684451461035193,0.07435557270240836,0.08050679107747571,0.08676710361996536,0.09303130625597153],[0.08148031091220807,0.07436920130450732,0.06713615972190902,0.059840803848521425,0.052554029394937925,0.045358908922695895,0.038351493442835664,0.03164146651933066,0.02535257921334063,0.019622678824208113,0.014602522365308694,0.010449534502916982,0.007300432445604361,0.00518114259541093,0.0038884728899116756,0.003247232100795872,0.003772086783923703,0.0059020773362917995,0.009225791161210594,0.013334026220685984,0.017953257242587246,0.02286611404984678,0.027884222909424935,0.032841659474528564,0.03759367454888238,0.042016673984433636,0.04600847274721404,0.04948864797864668,0.05239903885698587,0.05470450213692134,0.05639404246009296,0.05748241964011213,0.05801227989757938,0.058056725765723405,0.057721959639511156,0.057149112270990995,0.05651353697369661,0.05601887207417862,0.055882771185035436,0.05631281498558021,0.05747589994913761,0.05947061723181113,0.062314190101061505,0.06594931057906317,0.0702658853465494,0.07512704512208838,0.08039077208318701,0.08592385851204266,0.09160893335730277,0.09734675927549977],[0.08081745175594168,0.07362686793256955,0.06630851147426,0.058922267328748265,0.051539485888901164,0.0442439184433594,0.03713256561897544,0.030316412603125432,0.02392106933018471,0.018087455333237107,0.012972892492942995,0.008752671480287938,0.0056145507679729555,0.0036854825332407856,0.0027848012001367526,0.0026105797032608432,0.0035786772843339983,0.005965080409166866,0.009429655180675957,0.013651899598114772,0.018389397415526868,0.023436248593706528,0.0286099921682026,0.03374893222857148,0.038712021691814084,0.0433792328396244,0.0476519453229395,0.05145331334663317,0.054728684164358665,0.05744615532447203,0.05959733779486954,0.06119834577992348,0.06229095127333203,0.06294369984614578,0.06325255654491167,0.06334032391798734,0.06335369547823637,0.0634565630402123,0.06381846759449603,0.06459832797359552,0.0659258474113584,0.0678852924168533,0.07050680093486987,0.07376791870454653,0.07760396767739829,0.08192288367240669,0.08661989537242198,0.0915891365306302,0.09673132756967232,0.10195799113013986],[0.08058380262291716,0.07335704859766626,0.06599962822279061,0.05857154415206374,0.05114432239671467,0.04380193449935475,0.036641612340000095,0.029774516031140504,0.02332626192709855,0.017437492303275695,0.01226524171056083,0.007987549132149602,0.004815914539556582,0.002982008028831434,0.002444543903152518,0.0027929078822890373,0.004169509048708884,0.0067511730585605445,0.010333181647287014,0.014658300893600608,0.019502046156365117,0.024666464304139008,0.02997490031763692,0.035270755567922224,0.04041762881778454,0.04529973839684801,0.04982231105899318,0.05391190301124919,0.05751670036173608,0.06060685283049525,0.06317486724131817,0.06523603574173173,0.06682879484368054,0.06801479820596947,0.06887833619288215,0.06952456516283269,0.07007587624768317,0.07066575438751181,0.07142981769600137,0.07249450119096071,0.07396494295149479,0.07591456250837987,0.07837891081772272,0.08135528085768776,0.08480774776575259,0.08867574951587072,0.09288376725051178,0.09735011348531544,0.10199375056737563,0.10673890079072165],[0.0807935536656952,0.0735743927700185,0.06622437622736213,0.05880339850201544,0.05138280878937667,0.04404630209276159,0.03689070365144494,0.030026636495343206,0.023579183449849134,0.01768909249365026,0.012516631174348432,0.008255713669297771,0.005179789468552492,0.003671443842035057,0.0036909304748408375,0.004570535537521317,0.006210486897191424,0.00881421499658867,0.012359009150655577,0.01666209643458861,0.02151234034386914,0.026712150441571703,0.03208475512151094,0.03747470571243781,0.04274766501636419,0.047790301461506104,0.05251027372415779,0.05683624591261625,0.06071791240913551,0.06412602687953882,0.06705241650404639,0.06950992538312223,0.0715321733160809,0.07317294044999574,0.07450490269968393,0.07561736835753571,0.0766126442908679,0.07760075232642202,0.07869248528855777,0.0799912515690352,0.081584708451336,0.08353759573854057,0.08588717998803908,0.08864218672019968,0.09178521033209501,0.09527774549780323,0.09906653272902738,0.10308994997974393,0.10728355519245511,0.11158434818211657],[0.08145156037372787,0.07428344538424633,0.0669868815920023,0.05962148613247035,0.05225822005622816,0.044980313329888236,0.037884189362078,0.031080546394440856,0.024696138127009302,0.018877931614742563,0.013804582266223941,0.009717536205248898,0.006975073843934828,0.005933355104034761,0.006349175383018195,0.007586184757179132,0.00946483267086653,0.012107256111197718,0.015568173389771525,0.019758125437920496,0.024511880335393678,0.029647645036964446,0.0349930974203136,0.04039408518732556,0.04571704961562457,0.050849499767381845,0.05569993114430325,0.06019759828652021,0.06429225005217881,0.06795384160942082,0.07117219485665396,0.07395654321814664,0.07633485567678515,0.07835278885209289,0.08007207293679337,0.08156811376158267,0.08292661437623236,0.08423911490865191,0.08559753944189769,0.0870881115604911,0.0887852912671789,0.09074658040158692,0.09300902297281918,0.09558794447463727,0.09847800712697717,0.10165617947381525,0.10508590228910672,0.1087216585987791,0.1125132885814823,0.11640962788485956],[0.08255521422399932,0.07548111932762522,0.06828381038955159,0.061022720505793424,0.05376865748770787,0.04660494695443274,0.03962885468643379,0.032953753110644045,0.02671318223310304,0.02106945533524386,0.016231735635631652,0.01248455106834587,0.010175431132592195,0.009484636383931325,0.010109787203678857,0.011565434211637323,0.013642073418725368,0.016362620126752526,0.019771835595962385,0.02383430927945467,0.02843935382446267,0.03343896596571194,0.03867792877350594,0.04401002857786526,0.04930530513564868,0.054452881347722706,0.059361848250855984,0.06396133273755468,0.06820021808476572,0.07204669391977678,0.07548767829940399,0.07852808433743476,0.08118985807256514,0.08351068028381617,0.08554220326431006,0.08734769258846461,0.08899897662166334,0.09057268550547705,0.09214589059010414,0.0937914200196136,0.09557328653382106,0.09754276051261207,0.09973559959159341,0.10217078624450052,0.10485086287924152,0.10776367212537948,0.11088509688458711,0.11418230407143426,0.11761702821543886,0.12114854572293485],[0.08409559094770803,0.07715795548092685,0.0701056419770478,0.06299833071599559,0.05590740075860947,0.048917496441326334,0.04212873613419406,0.035660244038855406,0.02965625913979685,0.0242965131538165,0.01981016066358342,0.01647664121799484,0.01455433815029751,0.014091442179496674,0.01482390375756034,0.016393770332422158,0.01859458037052266,0.021380445947353537,0.024758297590934123,0.02870603581155569,0.033149702419034144,0.03797640870679191,0.043055722411745156,0.048256558159402045,0.05345745653339928,0.058551972441158784,0.06345115708803037,0.0680844725487661,0.07239988800435906,0.07636353330090352,0.0799590747306728,0.08318686118901694,0.08606282226816331,0.08861706168774378,0.09089207217634031,0.09294050210972957,0.0948224341636706,0.09660219551211777,0.0983448055482801,0.10011226826071787,0.10196000790432676,0.10393379682317702,0.10606750585047725,0.10838191188443955,0.1108846424743718,0.11357116484120117,0.11642658410786745,0.11942793640763966,0.12254665568157751,0.12575094378822735],[0.08605772763878612,0.07929804367247081,0.07243590696310295,0.06553185870395424,0.05865872286169526,0.05190364082491798,0.04537095469604279,0.03918647383806469,0.0335035922955658,0.028510350327116,0.024430830711141455,0.021500454569151485,0.01988590455296405,0.019573816567156753,0.020356075029254503,0.021966061687929885,0.024216585514955414,0.027024906340496174,0.030362611765369786,0.03420089540740903,0.03848292086011375,0.0431218009654693,0.04801127454099502,0.05303852582049047,0.05809435449216569,0.06307982241419487,0.06791006003053489,0.07251616157375403,0.07684589377070604,0.08086368141935428,0.08455013087304405,0.0879012183526216,0.0909271871470283,0.09365115014441867,0.09610737233860998,0.09833920813227871,0.10039668945224621,0.10233380177829186,0.10420554187221986,0.10606491362210185,0.1079600718043244,0.10993184997816678,0.11201189385423048,0.11422156120804715,0.11657165370006559,0.1190629368225126,0.12168730795972084,0.12442941018606085,0.12726846979670475,0.13018015454326964],[0.08842030716077363,0.08187814647144984,0.07524941332213433,0.06859600108635515,0.061992692638937544,0.05552945603859283,0.04931445668819655,0.04347783129066272,0.03817551075646062,0.03359006661196818,0.029920608561884575,0.027348668657855627,0.025975911244980356,0.025767785620552316,0.026564533223593666,0.028164017313235673,0.030403413485916807,0.033185181353786536,0.03645671939887164,0.040177395304802264,0.044295361024369206,0.048739606400170464,0.05342301618938975,0.05825015577015253,0.06312536619002389,0.06795918222641098,0.07267268427938872,0.07720009118411009,0.08149005968402613,0.08550609129644925,0.08922632735018537,0.09264290463259438,0.09576096466088961,0.09859735865837242,0.10117906354737047,0.10354131792013717,0.10572549822124074,0.10777678126439176,0.10974167502505405,0.1116655380493849,0.11359023900361395,0.11555212142578228,0.1175804267246421,0.11969628884748824,0.12191235243438697,0.12423299497994725,0.1266550677003794,0.12916902252050066,0.1317602709236178,0.134410624171177]],[],[],[[0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416,0.7393662298307416],[0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023,0.7476604752539023],[0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769,0.7558948849758769],[0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251,0.7640010940591251],[0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618,0.7719027074926618],[0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314,0.7795151881756314],[0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817,0.7867459078451817],[0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623,0.7934944030956623],[0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548,0.799652884610548],[0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704,0.8051070532254704],[0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008,0.8097372793623008],[0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281,0.813420195504281],[0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182,0.8160307042572182],[0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412,0.8174441940136412],[0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876,0.8175401385069876],[0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519,0.8162212267698519],[0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101,0.8134593592534101],[0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375,0.8093038936273375],[0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295,0.8038272190252295],[0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013,0.7971109013788013],[0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362,0.7892482272355362],[0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757,0.7803432323825757],[0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004,0.7705081519592004],[0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808,0.7598606207619808],[0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685,0.7485211496459685],[0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903,0.7366110253212903],[0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231,0.7242506313847231],[0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731,0.7115581358806731],[0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952,0.6986484755896952],[0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912,0.685632566099912],[0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289,0.6726166705866289],[0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678,0.6597018658276678],[0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798,0.6469835503510798],[0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282,0.6345509469091282],[0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669,0.6224865606147669],[0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466,0.6108655666544466],[0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146,0.5997551196358146],[0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921,0.5892136024173921],[0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527,0.5792898660841527],[0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413,0.5700225503193413],[0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672,0.5614396029837672],[0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136,0.5535581213548136],[0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039,0.5463846013366039],[0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967,0.5399156098158967],[0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722,0.5341388162056722],[0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906,0.529034264581906],[0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171,0.5245757533331171],[0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798,0.5207322079075798],[0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439,0.5174689661814439],[0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604,0.5147489299369604]],[[0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853,0.0806493406151853],[0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897,0.07343573973246897],[0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287,0.06609260788631287],[0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895,0.05867991153960895],[0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635,0.051269127329419635],[0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601,0.04394417565181601],[0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426,0.03680225816042426],[0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752,0.02995456637885752],[0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623,0.023526874059291623],[0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174,0.017660174478257174],[0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833,0.012511925209996833],[0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066,0.008259148379075066],[0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456,0.00510142304301456],[0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066,0.00321186868195066],[0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943,0.002462326806316943],[0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927,0.002517172236582927],[0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611,0.003701047554423611],[0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946,0.006209054057971946],[0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056,0.009748292728888056],[0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921,0.014031964182496921],[0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732,0.018829403183163732],[0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296,0.023940152653542296],[0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002,0.02918533314673002],[0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201,0.03440608789195201],[0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128,0.03946380781743128],[0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761,0.04424063553627761],[0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254,0.04863990946930254],[0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796,0.05258653850574796],[0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068,0.05602737976324068],[0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986,0.058931695702719986],[0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787,0.06129173870448787],[0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235,0.06312345891064235],[0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513,0.06446724708103513],[0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039,0.06538849391206039],[0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874,0.06597755773184874],[0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487,0.06634848974336487],[0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173,0.06663562848766173],[0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789,0.06698709672789789],[0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731,0.0675545725148731],[0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313,0.06847970582600313],[0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455,0.06987913629741455],[0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975,0.07183153248221975],[0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482,0.07437029099854482],[0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987,0.07748389901799987],[0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798,0.08112323584012798],[0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658,0.08521292568102658],[0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971,0.08966335148021971],[0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848,0.09438087250506848],[0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709,0.09927518828314709],[0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782,0.10426388004680782]],[],[]]},{"xaxis.title":"gamma","xaxis2.title":"gamma","xaxis.range":[-6.0,6.0],"xaxis2.range":[-6.0,6.0],"xaxis.type":"log","xaxis2.type":"log"}],"label":"gamma","method":"update"}],"direction":"up","x":0.35,"xanchor":"left","y":-0.29,"yanchor":"middle"},{"buttons":[{"args":[{"visible":[false,false,false,false,true,true,true,true]},{"yaxis.title":"gamma","yaxis.range":[-6.0,6.0],"yaxis2.range":[-6.0,6.0],"yaxis.type":"log","yaxis2.type":"log"}],"label":"gamma","method":"update"}],"direction":"up","x":0.35,"xanchor":"left","y":-0.43,"yanchor":"middle"}],"xaxis":{"anchor":"y","autorange":false,"domain":[0.05,0.45],"exponentformat":"e","range":[-9.0,6.0],"tickfont":{"size":11},"tickmode":"auto","title":{"text":"C"},"type":"log"},"yaxis":{"anchor":"x","autorange":false,"domain":[0,1],"exponentformat":"e","range":[-6.0,6.0],"tickfont":{"size":11},"tickmode":"auto","title":{"text":"gamma"},"type":"log"},"xaxis2":{"anchor":"y2","autorange":false,"domain":[0.6,1],"exponentformat":"e","range":[-9.0,6.0],"tickfont":{"size":11},"tickmode":"auto","title":{"text":"C"},"type":"log"},"yaxis2":{"anchor":"x2","autorange":false,"domain":[0,1],"exponentformat":"e","range":[-6.0,6.0],"tickfont":{"size":11},"tickmode":"auto","type":"log"},"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}}},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>

### Expected Improvement (EI)

In [60]:
ax_client = create_svc_client(botorch_acqf_class=ExpectedImprovement)
for i in range(10):
    parameterization, trial_index = ax_client.get_next_trial()
    ax_client.complete_trial(
        trial_index=trial_index, raw_data=evaluate_svc(parameterization)
    )
results_svc["EI"] = ax_client.get_trials_data_frame()

[WARNING 08-11 10:42:50] ax.service.ax_client: Random seed set to 1. Note that this setting only affects the Sobol quasi-random generator and BoTorch-powered Bayesian optimization models. For the latter models, setting random seed to the same number for two optimizations will make the generated trials similar, but not exactly the same, and over time the trials will diverge more.
[INFO 08-11 10:42:50] ax.service.utils.instantiation: Created search space: SearchSpace(parameters=[RangeParameter(name='C', parameter_type=FLOAT, range=[1e-09, 1000000.0], log_scale=True), RangeParameter(name='gamma', parameter_type=FLOAT, range=[1e-06, 1000000.0], log_scale=True)], parameter_constraints=[]).
[WARNING 08-11 10:42:56] ax.service.utils.report_utils: Column reason missing for all trials. Not appending column.


In [61]:
model = cast(
    TorchModelBridge,
    not_none(ax_client.generation_strategy.model),
)
fig = interact_contour_plotly(model=model, metric_name="accuracy")
fig.update_layout(dict(width=None, autosize=True))
render_plotly_html(fig)

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="ea8bdfac-9110-49e8-aa3a-fe05d4285828" class="plotly-graph-div" style="height:450px; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("ea8bdfac-9110-49e8-aa3a-fe05d4285828")) {                    Plotly.newPlot(                        "ea8bdfac-9110-49e8-aa3a-fe05d4285828",                        [{"autocolorscale":false,"autocontour":true,"colorbar":{"len":0.875,"tickfont":{"size":8},"ticksuffix":"","x":0.45,"y":0.5},"colorscale":[[0.0,"rgb(247,252,253)"],[0.125,"rgb(229,245,249)"],[0.25,"rgb(204,236,230)"],[0.375,"rgb(153,216,201)"],[0.5,"rgb(102,194,164)"],[0.625,"rgb(65,174,118)"],[0.75,"rgb(35,139,69)"],[0.875,"rgb(0,109,44)"],[1.0,"rgb(0,68,27)"]],"contours":{"coloring":"heatmap"},"hoverinfo":"x+y+z","ncontours":25,"visible":false,"x":[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],"xaxis":"x","y":[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],"yaxis":"y","z":[[0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072],[0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489],[0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062],[0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303],[0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806],[0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483],[0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406],[0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141],[0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177],[0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435],[0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241],[0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618],[0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997],[0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537],[0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573],[0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341],[0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242],[0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404],[0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176],[0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534],[0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034],[0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264],[0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956],[0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823],[0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617],[0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583],[0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319],[0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286],[0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292],[0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241],[0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515],[0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371],[0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735],[0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473],[0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315],[0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737],[0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509],[0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895],[0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897],[0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661],[0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306],[0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263],[0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815],[0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757],[0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384],[0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682],[0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287],[0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235],[0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307],[0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948]],"zauto":true,"type":"contour"},{"autocolorscale":false,"autocontour":true,"colorbar":{"len":0.875,"tickfont":{"size":8},"ticksuffix":"","x":1,"y":0.5},"colorscale":[[0.0,"rgb(255,247,251)"],[0.14285714285714285,"rgb(236,231,242)"],[0.2857142857142857,"rgb(208,209,230)"],[0.42857142857142855,"rgb(166,189,219)"],[0.5714285714285714,"rgb(116,169,207)"],[0.7142857142857143,"rgb(54,144,192)"],[0.8571428571428571,"rgb(5,112,176)"],[1.0,"rgb(3,78,123)"]],"contours":{"coloring":"heatmap"},"hoverinfo":"x+y+z","ncontours":25,"visible":false,"x":[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],"xaxis":"x2","y":[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],"yaxis":"y2","z":[[0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897],[0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808],[0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832],[0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514],[0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293],[0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873],[0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547],[0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497],[0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774],[0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342],[0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128],[0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446],[0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893],[0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456],[0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099],[0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063],[0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922],[0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748],[0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481],[0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475],[0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659],[0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487],[0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673],[0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931],[0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883],[0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147],[0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923],[0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243],[0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963],[0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885],[0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405],[0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294],[0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277],[0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464],[0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382],[0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644],[0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498],[0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927],[0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737],[0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282],[0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906],[0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147],[0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558],[0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169],[0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212],[0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031],[0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164],[0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128],[0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071],[0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513]],"type":"contour"},{"hoverinfo":"text","legendgroup":"In-sample","marker":{"color":"black","opacity":0.5,"symbol":1},"mode":"markers","name":"In-sample","text":["Arm 0_0\u003cbr\u003eaccuracy: 0.48 (SEM: None)\u003cbr\u003eC: 3.42871e-05\u003cbr\u003egamma: 0.000601517","Arm 1_0\u003cbr\u003eaccuracy: 0.496 (SEM: None)\u003cbr\u003eC: 55.3814\u003cbr\u003egamma: 5357.65","Arm 2_0\u003cbr\u003eaccuracy: 0.808 (SEM: None)\u003cbr\u003eC: 690.339\u003cbr\u003egamma: 0.00857996","Arm 3_0\u003cbr\u003eaccuracy: 0.78 (SEM: None)\u003cbr\u003eC: 562386\u003cbr\u003egamma: 0.000184708","Arm 4_0\u003cbr\u003eaccuracy: 0.776 (SEM: None)\u003cbr\u003eC: 923227\u003cbr\u003egamma: 0.0545368","Arm 5_0\u003cbr\u003eaccuracy: 0.812 (SEM: None)\u003cbr\u003eC: 8059.7\u003cbr\u003egamma: 0.00137448","Arm 6_0\u003cbr\u003eaccuracy: 0.8 (SEM: None)\u003cbr\u003eC: 657.413\u003cbr\u003egamma: 1e-06","Arm 7_0\u003cbr\u003eaccuracy: 0.792 (SEM: None)\u003cbr\u003eC: 410.754\u003cbr\u003egamma: 0.000125186","Arm 8_0\u003cbr\u003eaccuracy: 0.824 (SEM: None)\u003cbr\u003eC: 57567.2\u003cbr\u003egamma: 1e-06"],"visible":false,"x":[3.428714353076635e-05,55.38136172368294,690.33938400923,562386.4909845794,923227.2828835016,8059.70102430378,657.4126489790578,410.75370137586805,57567.15135812723],"xaxis":"x","y":[3.428714353076635e-05,55.38136172368294,690.33938400923,562386.4909845794,923227.2828835016,8059.70102430378,657.4126489790578,410.75370137586805,57567.15135812723],"yaxis":"y","type":"scatter"},{"hoverinfo":"text","legendgroup":"In-sample","marker":{"color":"black","opacity":0.5,"symbol":1},"mode":"markers","name":"In-sample","showlegend":false,"text":["Arm 0_0\u003cbr\u003eaccuracy: 0.48 (SEM: None)\u003cbr\u003eC: 3.42871e-05\u003cbr\u003egamma: 0.000601517","Arm 1_0\u003cbr\u003eaccuracy: 0.496 (SEM: None)\u003cbr\u003eC: 55.3814\u003cbr\u003egamma: 5357.65","Arm 2_0\u003cbr\u003eaccuracy: 0.808 (SEM: None)\u003cbr\u003eC: 690.339\u003cbr\u003egamma: 0.00857996","Arm 3_0\u003cbr\u003eaccuracy: 0.78 (SEM: None)\u003cbr\u003eC: 562386\u003cbr\u003egamma: 0.000184708","Arm 4_0\u003cbr\u003eaccuracy: 0.776 (SEM: None)\u003cbr\u003eC: 923227\u003cbr\u003egamma: 0.0545368","Arm 5_0\u003cbr\u003eaccuracy: 0.812 (SEM: None)\u003cbr\u003eC: 8059.7\u003cbr\u003egamma: 0.00137448","Arm 6_0\u003cbr\u003eaccuracy: 0.8 (SEM: None)\u003cbr\u003eC: 657.413\u003cbr\u003egamma: 1e-06","Arm 7_0\u003cbr\u003eaccuracy: 0.792 (SEM: None)\u003cbr\u003eC: 410.754\u003cbr\u003egamma: 0.000125186","Arm 8_0\u003cbr\u003eaccuracy: 0.824 (SEM: None)\u003cbr\u003eC: 57567.2\u003cbr\u003egamma: 1e-06"],"visible":false,"x":[3.428714353076635e-05,55.38136172368294,690.33938400923,562386.4909845794,923227.2828835016,8059.70102430378,657.4126489790578,410.75370137586805,57567.15135812723],"xaxis":"x2","y":[3.428714353076635e-05,55.38136172368294,690.33938400923,562386.4909845794,923227.2828835016,8059.70102430378,657.4126489790578,410.75370137586805,57567.15135812723],"yaxis":"y2","type":"scatter"},{"autocolorscale":false,"autocontour":true,"colorbar":{"len":0.875,"tickfont":{"size":8},"ticksuffix":"","x":0.45,"y":0.5},"colorscale":[[0.0,"rgb(247,252,253)"],[0.125,"rgb(229,245,249)"],[0.25,"rgb(204,236,230)"],[0.375,"rgb(153,216,201)"],[0.5,"rgb(102,194,164)"],[0.625,"rgb(65,174,118)"],[0.75,"rgb(35,139,69)"],[0.875,"rgb(0,109,44)"],[1.0,"rgb(0,68,27)"]],"contours":{"coloring":"heatmap"},"hoverinfo":"x+y+z","ncontours":25,"visible":true,"x":[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],"xaxis":"x","y":[1e-06,1.757510624854793e-06,3.0888435964774785e-06,5.428675439323859e-06,9.540954763499944e-06,1.67683293681101e-05,2.94705170255181e-05,5.1794746792312125e-05,9.102981779915228e-05,0.00015998587196060574,0.0002811768697974231,0.0004941713361323833,0.000868511373751352,0.0015264179671752333,0.0026826957952797246,0.004714866363457394,0.008286427728546842,0.014563484775012445,0.025595479226995333,0.04498432668969444,0.07906043210907701,0.1389495494373136,0.244205309454865,0.42919342601287785,0.7543120063354607,1.325711365590108,2.329951810515372,4.094915062380427,7.196856730011514,12.648552168552959,22.229964825261955,39.06939937054613,68.66488450042998,120.67926406393264,212.09508879201925,372.7593720314938,655.1285568595496,1151.3953993264481,2023.5896477251556,3556.4803062231213,6250.551925273976,10985.411419875572,19306.977288832455,33932.217718953296,59636.23316594637,104811.3134154683,184206.99693267164,323745.754281764,568986.6029018281,1000000.0],"yaxis":"y","z":[[0.4768731329347412,0.4755253693607116,0.47454994543099366,0.4739929085393086,0.4739016227380968,0.47432421635242356,0.4753089000604388,0.47690314697483505,0.479152731839036,0.4821006351176183,0.485785830062194,0.4902419868043849,0.4954961461608459,0.5015674345459795,0.50846590581502,0.516191600545808,0.5247339035333387,0.5340712548186973,0.5441712323150065,0.5549909835422759,0.5664779499685177,0.5785708069897874,0.5912005374572623,0.6042915638752391,0.6177628784974722,0.6315291261040331,0.6455016072877626,0.6595891784878974,0.6736990282032962,0.6877373073999765,0.7016095877031033,0.7152211162802317,0.7284768356622765,0.7412811463327041,0.7535374177478387,0.7651473074956263,0.7760100315157432,0.7860218301439025,0.7950759632289258,0.8030635934118483,0.8098759500279108,0.8154087822613035,0.8195692748982392,0.822284328513949,0.8235099685098549,0.8232420874042436,0.8215286025929815,0.8184742146323478,0.8142253922201969,0.8089510238160853],[0.473373063454019,0.4718763661183611,0.47075563969226997,0.47005876666282204,0.4698351773727626,0.470135296695335,0.471009850158852,0.4725090168490019,0.4746814213476184,0.4775729654625171,0.4812255136226994,0.4856754642320297,0.49095226253854796,0.4970769360901087,0.5040607560624316,0.5119041385406055,0.5205958910966301,0.5301128781796244,0.5404201288619978,0.5514713554435998,0.5632098067956466,0.5755693565436515,0.5884757246651835,0.601847745822633,0.6155986199524959,0.6296371026524241,0.6438686099830417,0.6581962223823566,0.672521575245121,0.6867456201607112,0.7007692323818728,0.7144936293256167,0.7278205559759806,0.7406521929035252,0.7528907618762407,0.7644378564986576,0.7751936229201638,0.7850560553864983,0.7939208159202293,0.8016820658990601,0.8082348796677311,0.813480096336799,0.8173315980582209,0.8197249537146074,0.820626929781777,0.8200458831601198,0.8180422165898518,0.8147305384788522,0.8102653067521226,0.8048213003572738],[0.4700235377784523,0.46838128460010287,0.4671180798260149,0.4662835670967987,0.4659291776805927,0.46610758247186324,0.4668719937726474,0.468275299663087,0.47036901756748306,0.4732020612616865,0.47681932870885796,0.4812601383712768,0.4865565696909347,0.49273179734615397,0.49979854223029163,0.5077577831777994,0.5165978683967776,0.5262941260396228,0.5368090050393289,0.5480927008659118,0.5600841614383836,0.5727123417273484,0.5858975812983661,0.5995530055076568,0.6135858842634551,0.6278989120179669,0.6423913939448014,0.6569603348224883,0.6715014295748141,0.6859099489059971,0.7000815013967495,0.7139126366744671,0.7273012361769615,0.7401466250979267,0.7523493433991445,0.7638105550603881,0.7744311785534259,0.784111004638151,0.792748304296835,0.8002406328766785,0.8064876357151798,0.8113964848856665,0.8148896929477251,0.8169142555834189,0.8174512662650016,0.8165253705018625,0.8142119236673402,0.8106357529329195,0.8059579178966036,0.8003571925465778],[0.46684794456721357,0.465065138620231,0.46366393631310393,0.46269564762644594,0.4622136130569515,0.4622726669559672,0.4629284428736184,0.4642364991971612,0.4662512455780474,0.46902465662450155,0.4726047713412023,0.4770339976191195,0.4823472732169698,0.4885701781478473,0.49571714200010203,0.5037899276927517,0.512776577210815,0.5226509567858253,0.5333729436981622,0.5448891877736426,0.5571343004130189,0.5700322963702527,0.5834981329668237,0.5974392356343242,0.6117569459904973,0.6263478666732132,0.6411051019920517,0.655919405764249,0.670680249458221,0.6852768166967075,0.6995989153897917,0.7135377771905574,0.7269866873574163,0.739841361080471,0.7519999659327075,0.7633627074876252,0.7738309872348721,0.7833063614139519,0.7916898942241006,0.7988828906329232,0.8047900942832796,0.8093258842269825,0.8124229043487302,0.8140417703908118,0.8141804901098544,0.8128822165690227,0.8102388719168767,0.8063869356662279,0.8014943064727208,0.7957427415008578],[0.463868859074413,0.4619521545932106,0.4604191348778763,0.4593226623059485,0.4587178694683405,0.45866163901390955,0.45921191999343003,0.46042685486664153,0.4623636916239913,0.46507745904132886,0.4686193925559692,0.4730351175820095,0.4783626312412478,0.48463017625626437,0.49185416895992856,0.5000374081943233,0.5091678157248481,0.5192179032596635,0.5301450252544819,0.5418923161627951,0.554390101263456,0.567557547498123,0.5813043654537953,0.5955324436424446,0.610137360040163,0.6250097610500681,0.640036624494985,0.6551024349168366,0.6700903001443572,0.6848830300319381,0.6993641822162502,0.713419055490474,0.7269355787686544,0.7398050041917116,0.751922273823351,0.7631859112436321,0.7734973415570673,0.7827597611939048,0.7908771720867125,0.797754875471794,0.8033029739052464,0.8074435011641173,0.81012012870719,0.8113084249522705,0.8110247274676968,0.8093318611837279,0.8063395872579641,0.8021977511396923,0.7970823263534553,0.7911780587661557],[0.4611075803276666,0.4590652618060343,0.45740829838945246,0.4561909748042117,0.45547007581768617,0.4553043863080964,0.4557540246971662,0.45687958055600997,0.45874102550130086,0.4613963671729889,0.4649000217166402,0.4693008954305624,0.47464019856323003,0.48094907311046753,0.48824620672606095,0.4965357100902878,0.5058055991045668,0.5160271672575083,0.527155335051547,0.5391298184610889,0.5518768082945362,0.5653108493212575,0.5793366973833001,0.5938510376699175,0.6087440272471274,0.6239006735079479,0.6392020849193084,0.6545266396968179,0.6697511172784423,0.6847518291325955,0.6994057697676019,0.7135917845803293,0.7271917163869979,0.7400914454821955,0.7521816803160384,0.7633582989658496,0.7735220261439544,0.7825773714365218,0.7904312948821587,0.7969931669122943,0.8021783844707336,0.8059166333053988,0.8081629251355072,0.8089083399870389,0.8081880851056317,0.8060851593785883,0.8027280755210526,0.7982816121796613,0.7929313937598251,0.7868658336850293],[0.4585836496096847,0.4564255552219679,0.45465415026256084,0.4533249996884061,0.4524963820347174,0.4522288115286888,0.45258439254107646,0.4536259748507467,0.455416074783535,0.45801552510714133,0.4614818176705357,0.4658671115475701,0.47121590469666746,0.47756242441922914,0.4849279005216799,0.49331804518632105,0.5027212045287568,0.5131076133107647,0.5244298876834139,0.5366245004706698,0.5496137804812196,0.5633080287738945,0.5776075089490613,0.5924042143641062,0.6075834046103519,0.623024948387983,0.6386045288149351,0.6541947725353524,0.669666361754523,0.6848891805341767,0.6997335329526144,0.7140714490450131,0.7277780614794218,0.7407329875435497,0.7528215835219733,0.7639358525641632,0.7739746999407958,0.7828432210167416,0.7904510863084444,0.7967115881460501,0.8015450396945202,0.8048884667649013,0.8067082222655502,0.807011014027068,0.8058509036824534,0.8033310042700371,0.7995989084219484,0.7948353588807233,0.7892370484158989,0.7829969976045822],[0.4563143675689017,0.4540517499017149,0.45217689990424037,0.4507465130434648,0.4498201901010837,0.4494599810821808,0.44972976195939146,0.45069441141986527,0.45241875016625394,0.454966200903697,0.4583971241102488,0.4627667860903242,0.46812292934269006,0.4745029592425939,0.48193087198547524,0.4904142680842908,0.49994207287542225,0.510483638963503,0.5219894542368279,0.5343930235338619,0.54761323295119,0.561556688840716,0.5761198000126517,0.5911905503997392,0.6066499925022353,0.622373524012451,0.6382320201031422,0.6540928949428495,0.669821162833659,0.6852805629571237,0.7003348010845806,0.7148489442814963,0.7286909765767524,0.7417334790215119,0.7538553292844075,0.7649432167240925,0.7748926364258573,0.7836078797961952,0.7910005453898564,0.7969874281597463,0.8014932023279684,0.8044619969052734,0.8058716268373467,0.805744437874879,0.8041529826879946,0.8012198501221107,0.7971111808331126,0.7920237101741968,0.7861659451540843,0.7797363400471893],[0.45431433119648906,0.45195965142963607,0.4499936378352924,0.44847396311942417,0.4474613711320791,0.4470192404495538,0.447212982047129,0.44810923770825034,0.44977484057224143,0.4522754935037263,0.4556741151728149,0.4600287991998048,0.4653903327586328,0.4717992416743398,0.47928241243301517,0.48784958927036537,0.49749052726741916,0.5081738869447125,0.5198482700264543,0.532444626900841,0.5458789985000629,0.5600550250729128,0.5748660609723337,0.5901969084737124,0.6059252384001959,0.6219227791528404,0.638056357325183,0.6541888711855794,0.6701802751944235,0.6858886493389271,0.7011714201273633,0.7158867880698055,0.7298953951732242,0.7430622287520938,0.7552586949006659,0.7663646934499879,0.7762703730932536,0.7848770357417135,0.7920964155235881,0.7978479266962543,0.8020602670977934,0.8046851312155512,0.805712349476806,0.805179944479855,0.8031783426718839,0.7998484187334189,0.7953733373962104,0.7899644122159285,0.783841345255066,0.777208296423801],[0.452595014825889,0.45016167106112853,0.4481177744033432,0.44652182065837964,0.4454355141402054,0.44492334743354384,0.4450520165515312,0.44588963802667964,0.44750472901342564,0.449964905271887,0.4533352449360901,0.4576762584530958,0.46304139811616934,0.4694740394453159,0.4770038975545401,0.4856430290807928,0.4953822545351635,0.5061897528468087,0.5180125987388904,0.530779800506744,0.5444053545423111,0.5587908297574768,0.5738274533789184,0.5893977739915696,0.6053769936504646,0.6216340601251467,0.6380326071656801,0.6544318278283632,0.6706873636426182,0.6866522901975072,0.7021782763879832,0.71711698793164,0.7313217920201461,0.7446497924044209,0.7569641714828653,0.7681367202214205,0.7780502739289045,0.7866005200453621,0.7936963095383701,0.7992577624010346,0.8032183047039616,0.8055386367732565,0.80622142382142,0.8053203472342096,0.802942876467031,0.7992465620580966,0.7944292572851154,0.7887139895736391,0.7823289367087695,0.7754827995755513],[0.45116442052442834,0.4486664166503261,0.446558560083926,0.44490001525447526,0.44375326269083515,0.44318369070779984,0.44325902337822226,0.44404855131877335,0.44562212631255305,0.44804887448402325,0.45139557552622267,0.45572464725159034,0.4610916654388712,0.4675423389052224,0.4751088528601588,0.48380554175485824,0.49362448041819773,0.5045336399392226,0.5164791545709053,0.5293889631056192,0.5431760065371976,0.55774079205652,0.5729734142862409,0.5887551383083389,0.6049596432474076,0.6214540194171069,0.6380996078687218,0.6547527685995074,0.6712656624084586,0.6874871309444187,0.703263759031861,0.718441201328934,0.7328658488051655,0.7463868936848426,0.7588588133802093,0.7701442143090879,0.7801168222191944,0.7886641405517599,0.7956890092101105,0.801110175934095,0.8048666543761387,0.8069297017066401,0.8073156216269812,0.8060936110945064,0.8033871481928878,0.7993685118673794,0.7942473538678941,0.7882546750463373,0.7816227377748989,0.774561276254639],[0.4500268221218676,0.44747838979338866,0.4453207257274702,0.4436135062494461,0.44241980090519223,0.44180567151662037,0.4418396078098128,0.44259176607745077,0.44413297181217626,0.44653344091443403,0.4498611668275291,0.45417991266010027,0.4595467378816871,0.4660089783619589,0.47360058619175377,0.4823377223147444,0.49221376234025743,0.5031969668973293,0.5152334907441088,0.5282513093326076,0.542163398987488,0.556870247503118,0.5722618122919043,0.58821903273289,0.6046149951905655,0.621315843152961,0.6381815208955206,0.6550664368271488,0.6718201319982682,0.6882880398425232,0.7043124245839557,0.7197335869484864,0.7343914250454268,0.7481274317715264,0.7607871900477773,0.7722233781819785,0.7822991943475006,0.7908919425513449,0.7978964801021795,0.8032290917088368,0.806834114722313,0.8086940387938868,0.808839313660642,0.8073542433718848,0.8043769469222579,0.8000920138942876,0.7947174333028779,0.7884879615145483,0.7816355078345503,0.7743679309425789],[0.4491826232914164,0.446597815369821,0.4444042765892694,0.442662032250267,0.4414345467379984,0.4407883252824246,0.44079235193540833,0.4415173300726497,0.4430346861715071,0.4454152912467023,0.4487278470346495,0.45303687567995116,0.4584002421554715,0.4648661277909763,0.47246936102812437,0.4812270032115027,0.4911334539223847,0.5021582233240588,0.5142487326340182,0.5273341655305684,0.5413286164337667,0.5561335629914399,0.5716397779173333,0.5877287858975786,0.6042739631309146,0.621141371049542,0.6381904117524657,0.6552743905160434,0.6722410702665004,0.6889333039258665,0.7051898328462721,0.7208463427918697,0.7357368725701509,0.7496956735417478,0.7625596194116508,0.7741712634155691,0.784382636698714,0.7930599004837093,0.80008907633257,0.805383271495582,0.8088914470497237,0.810607178754112,0.8105749957098343,0.8088933574434447,0.805713031632973,0.8012277960485743,0.7956600342508202,0.7892441944267365,0.7822086686878165,0.7747580747003207],[0.44862834363439114,0.44602062173517243,0.44380446426962006,0.4420400715279507,0.4407910962230427,0.44012424317230076,0.44010870419428105,0.440815394289801,0.442315949581492,0.4446814410795208,0.44798075102999285,0.45227855031839015,0.4576328062426605,0.46409174106291906,0.4716901620214405,0.4804451737282393,0.4903519741698231,0.5013821013827731,0.5134853830126482,0.5265933219124701,0.5406221599499128,0.5554753197835461,0.5710452853131174,0.5872150180608179,0.603859004694856,0.6208440259354093,0.6380297332807165,0.6552691178833842,0.6724089555147973,0.6892903128432734,0.7057492032583684,0.7216174854641351,0.7367241058677292,0.7508967986391892,0.7639643808852521,0.7757598282417055,0.7861244164389551,0.7949134008044095,0.8020038998762679,0.80730526944715,0.8107702538562417,0.8124029279672602,0.8122613057204917,0.8104565075953654,0.8071489868413954,0.8025377687141293,0.7968456322273144,0.7903033857686126,0.7831338757353957,0.7755375986730004],[0.44835673820764843,0.44573857895299684,0.4435119466980532,0.4417370273603764,0.4404774384727117,0.4397998219253496,0.4397732703306976,0.44046855281629615,0.44195710047255776,0.4443097053811003,0.44759488019953664,0.4518768181288561,0.4572128876302126,0.4636506003480605,0.4712240379391584,0.4799499408152639,0.48982429680322187,0.5008209457299145,0.5128928236123189,0.5259746553452952,0.539985747579738,0.5548323442092603,0.570409467711998,0.5866023014972276,0.6032871957579605,0.6203323824982884,0.6375984840548824,0.6549388982226819,0.6722001432383801,0.689222247828337,0.7058392757656285,0.7218800818745912,0.7371694093477552,0.7515294614003083,0.764782123897874,0.7767520999380182,0.7872713765470207,0.79618570959187,0.8033641003929337,0.8087118532585887,0.8121846236939724,0.8137960507251933,0.81361623564172,0.811766685627441,0.8084136867098644,0.8037572212442756,0.7980168161919726,0.7914170343251861,0.7841737205506032,0.7764824582310796],[0.44835704641626745,0.4457395901157028,0.44351313010129106,0.44173763082239226,0.44047643203574616,0.43979582996735844,0.43976449017130176,0.4404526578088999,0.4419311257490936,0.4442699152212043,0.44753661833977687,0.45179434849856376,0.45709924886023023,0.4634975370526174,0.4710221590700863,0.4796893707977884,0.4894959798359545,0.5004181813868482,0.5124123159385751,0.5254169013773913,0.5393550149086623,0.5541364605805583,0.5696595272546219,0.5858123236660477,0.602473743264893,0.6195141320792957,0.6367957386100348,0.6541730266990007,0.6714929342703706,0.6885951644678704,0.7053126022504805,0.7214719607578477,0.7368947810179685,0.7513989420693344,0.7648008975126996,0.7769189570374162,0.7875781008436737,0.796617064076115,0.8038987144867847,0.8093247769240262,0.8128530488717672,0.8145052155366432,0.8143606103590453,0.8125473513761361,0.8092335678184255,0.8046163933317149,0.7989090203624019,0.7923276983453094,0.785080068131861,0.7773559823974061],[0.4486153569616472,0.44600811885668074,0.4437906712512149,0.44202253276553394,0.4407665052326172,0.4400882394280905,0.44005563078706256,0.4407380112840685,0.4422050990669111,0.44452566329446574,0.4477658593930079,0.45198719315522,0.45724408908975067,0.4635810872891846,0.4710298054755373,0.4796060047905905,0.4893073257828849,0.5001122765556394,0.5119806576368671,0.5248550508314949,0.5386627556992403,0.5533176884258543,0.568721996802613,0.5847673167780358,0.6013356845145056,0.6183001567994459,0.6355252089773643,0.6528669872798456,0.6701734980059564,0.6872848226746209,0.70403345830511,0.7202448979983367,0.7357385929840169,0.7503294796880109,0.7638303238465556,0.7760552405929547,0.7868249047319983,0.7959741630612556,0.8033629570457864,0.8088915658092217,0.8125195115685131,0.8142734650399649,0.8142373657608806,0.8125412980756925,0.8093513724101764,0.8048587962046072,0.7992680784799335,0.7927855811783207,0.7856097186442825,0.77792376504695],[0.4491150678259555,0.4465257263832132,0.4443241058156595,0.44256904070114306,0.4413225223621022,0.44064924675093164,0.44061599158471004,0.4412907902504878,0.44274186674073834,0.4450362941562882,0.4482383413933023,0.4524074830919492,0.457596075395156,0.4638467583848941,0.47118974956848453,0.47964033441878373,0.48919697189639016,0.4998403878593123,0.5115337667829057,0.5242238146259341,0.5378422796767284,0.5523075477233769,0.5675260661723458,0.5833934863446452,0.5997955031058586,0.6166084213228664,0.6336995051005804,0.6509271806153141,0.6681411740673326,0.6851826772580956,0.7018846477610938,0.7180723718271086,0.7335644501964882,0.7481744155283173,0.7617132621947645,0.7739932711818267,0.7848336454691955,0.7940686199870934,0.8015588323127782,0.807206658390347,0.8109734600494928,0.812886096271865,0.813027757791333,0.8115258438338229,0.8085408829577663,0.8042556323600999,0.7988642011215924,0.7925619605692438,0.7855373042629668,0.7779661079822225],[0.44983741499687224,0.4472716850138472,0.4450905610716087,0.44335194743747786,0.44211674761304137,0.44144839387761725,0.44141220706601386,0.4420745565172566,0.44350178865448414,0.44575889380941464,0.4489078873400146,0.4530058973279394,0.458102983966047,0.4642397727419547,0.47144506646906303,0.4797336919699619,0.48910488547355513,0.4995414629584829,0.5110098447088438,0.5234607884977863,0.5368305493744745,0.5510421730938033,0.5660067045216561,0.581624187837284,0.5977844140286164,0.6143674244506029,0.6312438125733206,0.6482748876181784,0.6653127801916914,0.6822005860447223,0.6987726634032866,0.7148552253954409,0.7302674057539041,0.7448230275063177,0.7583333748095582,0.7706113588060812,0.7814775726430966,0.7907688204997196,0.7983496732086666,0.8041269017627359,0.8080633101849375,0.8101825954608505,0.8105625493154677,0.8093236274613257,0.8066175245786565,0.8026163579008113,0.797502507710799,0.7914596190217024,0.7846655663543145,0.7772881570718656],[0.45076204120331337,0.44822363275818256,0.4460655090798874,0.4443443970130578,0.44311983910137526,0.4424537063459649,0.4424095444276287,0.44305172673478754,0.44444438801720426,0.44665011638684826,0.44972839125569924,0.45373377426666944,0.45871389352046943,0.46470731086318573,0.4717414231848049,0.47983060340740386,0.4889748024578764,0.4991587793433573,0.5103520043043402,0.522509137603212,0.5355708872056048,0.5494650243060641,0.5641073728356919,0.579402653278987,0.5952451244211518,0.6115190168706351,0.6280987885937626,0.6448492593010327,0.6616257021971075,0.6782739926227688,0.6946309370776781,0.7105249362396355,0.7257771749077319,0.7402035827874291,0.7536178733134187,0.7658360384191402,0.7766827357330358,0.785999988676895,0.7936583312172683,0.7995694288879939,0.8036967479396053,0.8060591865366079,0.8067261717141514,0.8058078964224932,0.8034444579822576,0.7997954248343352,0.7950303346321288,0.7893205878624003,0.7828333407097918,0.7757280233234842],[0.451867576243219,0.4493582346423738,0.44722351901025786,0.4455187383766755,0.4443018140648072,0.44363277906111837,0.4435731164992705,0.4441849147033793,0.4455298185241393,0.4476677627714212,0.4506554854796162,0.4545448389635701,0.45938094700677634,0.46520029634399185,0.47202889340955284,0.47988064860566126,0.48875615018056157,0.49864194383839916,0.5095103479748965,0.5213197368369827,0.5340151513527203,0.5475290710308491,0.5617821971520481,0.5766841394908832,0.5921339475271051,0.6080204714029821,0.6242225742571953,0.6406092471469524,0.6570397035419822,0.6733635556210945,0.6894212023097268,0.7050445916530382,0.7200585594282884,0.7342829919185776,0.7475361096700348,0.7596392077573696,0.7704231813609416,0.779737026111172,0.7874580417601648,0.7935024268128006,0.7978335106008363,0.8004645207071508,0.801454986823006,0.8009027649919955,0.7989343669590439,0.7956953177653869,0.791341404863732,0.7860313785745153,0.7799216231172271,0.7731632857801911],[0.45313220304394064,0.4506518204343489,0.4485389732810417,0.44684732615148554,0.4456329392534185,0.4449537591857756,0.44486895671175075,0.4454380934154347,0.4467201028321395,0.4487720791001622,0.4516478788431892,0.4553965611636103,0.46006071657181186,0.46567476618642945,0.4722633413981969,0.4798398709169911,0.48840549495418534,0.4979483888214896,0.5084435161012217,0.5198527628209988,0.5321253506336083,0.54519840296456,0.5589975442605419,0.5734374397681792,0.5884222200963232,0.6038457725145833,0.6195919154006715,0.635534502941707,0.6515375355624389,0.6674553797219892,0.6831332306968811,0.6984079850749249,0.713109725845035,0.7270640593165673,0.7400955710768452,0.7520326676248046,0.7627139984584018,0.7719964302585351,0.7797640584016732,0.7859369561958045,0.7904776113146734,0.7933930952024266,0.7947323904703066,0.79458000834435,0.7930477484388294,0.7902661518998734,0.78637665234624,0.7815250823837447,0.7758570312682922,0.7695153717886826],[0.4545341876989278,0.45208097410424264,0.44998671997364076,0.448303238397065,0.4470845146801943,0.44638619404405955,0.4462649261044706,0.44677755235374855,0.4479801275687148,0.44992677414957655,0.4526683807476558,0.45625117362110623,0.46071521030657264,0.46609286778615977,0.47240741619893173,0.4796717771191704,0.487887555689717,0.49704440586686294,0.5071197424630691,0.5180787641946816,0.5298747122382472,0.5424492684036756,0.5557329979611081,0.5696457600350135,0.5840970362902147,0.5989861601928097,0.6142024607105319,0.629625364642228,0.6451245311764855,0.6605601217894592,0.6757833390605857,0.6906373993304394,0.7049591343184667,0.7185814402484059,0.7313367976984316,0.7430620485066782,0.7536044990303699,0.7628291689309479,0.7706265833400973,0.7769199775553474,0.7816704226619108,0.7848785942690903,0.7865827994844827,0.7868539462238355,0.7857887355941895,0.783502350549952,0.7801216185875529,0.7757793318441945,0.7706101690877456,0.7647483262242677],[0.4560523566354726,0.45362305675403714,0.4515426422295303,0.4498608917543588,0.44862953190923677,0.4479017276218906,0.4477314404795667,0.4481726451429545,0.4492783993244691,0.45109977087714603,0.45368463691619887,0.4570763844646444,0.4613125587999278,0.4664235219940172,0.4724311961096983,0.4793479683732784,0.4871758255098398,0.4959057605090962,0.5055174611389951,0.5159792532384229,0.5272482420588513,0.5392705782467924,0.5519817736540618,0.5653070041186756,0.579161357566601,0.5934500120416641,0.6080683565785981,0.6229020966950617,0.6378274153187745,0.6527112892573104,0.6674120906033263,0.6817806302966751,0.6956618237112,0.7088971681168227,0.721328206005777,0.7328010858232552,0.74317219496129,0.7523146040094386,0.7601247325446551,0.7665283103282136,0.7714845501557269,0.7749876666697515,0.7770654735109578,0.7777754927483523,0.7771994735073816,0.7754373201891979,0.7726012898281952,0.7688110881917922,0.7641902242375234,0.7588636017647452],[0.45766650915156337,0.45525665106138935,0.45318413305640937,0.4514965436078064,0.45024319883163094,0.44947464130443276,0.44924201857155044,0.4495963351127357,0.45058757687397616,0.452263715126652,0.4546696064670042,0.45784581781271183,0.46182741811127165,0.4666427900271652,0.47231252219245917,0.4788484425784309,0.4862528440071441,0.49451793379297676,0.5036255138636508,0.5135468706835358,0.5242428318017708,0.5356639324735308,0.5477506335494965,0.5604335400515073,0.5736335862293229,0.5872621746732909,0.6012212819739694,0.6154035700283067,0.629692569601391,0.6439630305281171,0.6580815598139989,0.6719076923441737,0.6852955540894674,0.6980962764044243,0.710161289881846,0.7213465511529382,0.7315176199870322,0.7405553018849746,0.7483613282508823,0.7548633372500031,0.7600183605876999,0.7638142092320779,0.7662685633985225,0.7674260499005641,0.7673539409448016,0.7661372394806806,0.7638738574396872,0.7606704180935595,0.756638960400047,0.751894491145364],[0.4593577583458595,0.45696192097098404,0.4548904705985024,0.4531886784193867,0.45190333110874137,0.45108224306165806,0.4507736604286064,0.45102555365069746,0.4518848003827652,0.45339626765488683,0.45560181074177253,0.45853921594170516,0.46224112420402685,0.46673398058321564,0.4720370587369614,0.4781616081215658,0.4851101629946756,0.4928760371701637,0.5014430088705064,0.5107851796148606,0.5208669739181375,0.5316432359399836,0.5430593768076345,0.5550515321258932,0.5675467019333713,0.5804628633169102,0.5937090674093503,0.6071855562999744,0.620783960503206,0.6343876629911591,0.6478724396527288,0.6611075052502766,0.6739571032155443,0.6862827689885114,0.697946359569635,0.7088138653201332,0.7187598966444259,0.7276725736163117,0.7354583700786934,0.7420463330494985,0.7473910851992149,0.7514741685450952,0.7543035778767028,0.7559116670657479,0.7563518754669818,0.7556948462058393,0.7540244899477013,0.7514344187668455,0.7480249668126862,0.7439007607188332],[0.4611087976606734,0.45872088514907383,0.4566430942413389,0.4549182811033307,0.45359061633632614,0.45270511497117055,0.4523070702325014,0.452441390128303,0.453151840763786,0.4544802064320814,0.45646538376309365,0.4591424349469572,0.46254163232605733,0.46668753214942055,0.47159811752305286,0.4772840482909137,0.48374804813665806,0.49098444707049815,0.4989788823165538,0.5077081450089952,0.517140146877862,0.527233972633925,0.5379399814345024,0.549199924894872,0.5609470589832437,0.5731062417172719,0.5855940267053596,0.5983187832030392,0.6111808955022789,0.6240731169231738,0.636881174490487,0.6494847362829557,0.6617588593006118,0.6735760243153809,0.6848088270389809,0.6953333245514909,0.7050329302753594,0.7138026195739527,0.7215530780357594,0.7282143382393369,0.7337384533121645,0.7381008701788875,0.7413003726493224,0.7433577041279561,0.7443131789748555,0.7442236995791597,0.7431595987810788,0.7412016377153072,0.7384383342279139,0.734963616819799],[0.46290409372340496,0.46051760650384965,0.4584257859322291,0.4566690043862479,0.45528876089950227,0.4543272324458493,0.45382674052680577,0.45382913393895197,0.4543750929934926,0.45550336578270545,0.4572499530542427,0.4596472643289452,0.46272327328171264,0.4665007040984151,0.47099628149025474,0.47622007448182724,0.48217495770519675,0.4888562041947596,0.49625121184283166,0.5043393535851879,0.513091931059491,0.5224722046541095,0.5324354706480943,0.5429291588981772,0.5538929319865211,0.5652587782480437,0.5769511058527637,0.5888868623293494,0.6009757227472322,0.6131204091315333,0.6252172218124127,0.6371568773861208,0.6488257532499639,0.6601076290458969,0.6708859837399175,0.6810468478645676,0.690482123429924,0.6990931789038929,0.706794425796847,0.7135165186272725,0.7192088220109061,0.7238408711490658,0.7274027009171382,0.7299040942084942,0.7313729530916065,0.7318530884555075,0.7314017389772155,0.7300870736787205,0.727985825439452,0.7251810806779108],[0.4647300088798796,0.4623383029043042,0.46022476394169914,0.4584272398088299,0.45698453188875243,0.4559359704313689,0.4553209160476945,0.45517818963481443,0.45554543687279664,0.45645843796641444,0.4579503781722658,0.4600510993827861,0.4627863569898464,0.4661771086762881,0.4702388619667719,0.4749811048030159,0.48040683798531514,0.4865122204619374,0.4932863291019246,0.5007110250901934,0.5087609108896685,0.5174033560957128,0.5265985683252097,0.5362996868956338,0.5464528823677749,0.5569974536572596,0.5678659258375964,0.5789841654097106,0.590271545123862,0.601641206663057,0.6130004854078852,0.6242515749471872,0.63529251640517,0.6460185937900992,0.6563241950579983,0.6661051538250743,0.6752615173655878,0.6837005999132691,0.691340094305883,0.6981109554949919,0.7039597609920459,0.7088503074753874,0.7127643102694333,0.7157012050823011,0.7176771732914153,0.7187235930467174,0.7188851431940113,0.7182177570647267,0.7167865547091078,0.7146638022742167],[0.4665748588089146,0.4641713862118742,0.46202869815979575,0.4601821036627474,0.4586677077265051,0.45752201264290693,0.45678145559888467,0.4564818858183963,0.4566579878654339,0.4573426615505982,0.4585663728239304,0.4603564937009024,0.46273665214977094,0.4657261144157309,0.4693392219751293,0.47358490288713045,0.4784662727265962,0.4839803338984016,0.49011777466848216,0.4968628616731249,0.5041934130338772,0.5120808344377508,0.5204901982909182,0.5293803466214424,0.5387040017735215,0.5484078748589281,0.5584327700697075,0.5687136929823842,0.5791799826357257,0.5897555001985675,0.6003589210396589,0.6109041909629841,0.6213012190606648,0.6314568849279991,0.6412764305810058,0.650665279985778,0.6595312766849757,0.6677872551633156,0.6753537784485727,0.682161807121995,0.6881550386232627,0.6932916844775661,0.697545531769739,0.7009062414535356,0.7033789399922808,0.7049832364743518,0.7057518305732973,0.7057288673469124,0.7049681548865778,0.7035313102874218],[0.46842891197577435,0.46600743800903827,0.46382865711200527,0.46192534998164114,0.46033095163179644,0.4590791799785259,0.45820361004317867,0.457737197658029,0.45771175951003423,0.45815741954339506,0.45910203491505414,0.46057061752633544,0.46258476924416747,0.4651621498714539,0.4683159963863756,0.4720547097516892,0.47638152172829384,0.48129424890613104,0.48678513512942023,0.49284077734992215,0.4994421244446269,0.506564534348044,0.514177872443305,0.5222466337516382,0.5307300730431072,0.5395823303865963,0.5487525446350943,0.5581849537494623,0.5678189887408152,0.5775893776719752,0.5874262881481701,0.597255551523083,0.6069990292846056,0.6165751992020299,0.6259000494794267,0.6348883628877511,0.643455438102063,0.6515192272667704,0.6590027773324554,0.6658367748219896,0.6719619420950078,0.6773310388334722,0.6819102833738507,0.6856801025384378,0.6886352159716724,0.6907841367609363,0.6921482111270222,0.6927603256420436,0.6926633901791578,0.6919086736961876],[0.4702843385224884,0.46783913110536784,0.46561799737126874,0.46365122293386263,0.4619696219688732,0.46060419382795426,0.45958573372965095,0.4589444018435753,0.4587092576132675,0.4589077688089384,0.4595653073502146,0.4607046461203684,0.4623454725028393,0.46450393491060293,0.46719223791272263,0.47041829957262654,0.4741854813474327,0.47849239659085385,0.48333279875527524,0.4886955453126709,0.4945646287438726,0.5009192621460997,0.5077340043980845,0.5149789085333693,0.5226196769605596,0.5306178082687921,0.5389307223832219,0.5475118537322229,0.556310706115268,0.5652728689140104,0.5743400036827431,0.5834498251627196,0.592536123500077,0.6015289049685553,0.610354761349849,0.6189375990055813,0.6271998458796629,0.6350641903756594,0.642455794432111,0.6493047990844291,0.65554885431322,0.6611353898452885,0.6660233985260732,0.6701845998710144,0.673603952643937,0.6762795655231131,0.6782221024170983,0.6794537944956259,0.6800071631477133,0.6799235390086962],[0.47213511660434654,0.46966110614958734,0.4673922060846446,0.46535626076442965,0.46358153305934463,0.46209638925774316,0.46092894568277615,0.4601066815886877,0.45965602505708547,0.4596019208043803,0.4599673908567133,0.4607731007303896,0.46203694484002295,0.4637736651243955,0.46599451616689275,0.4687069883216763,0.471914597588776,0.4756167473921972,0.4798086632995908,0.4844813974445593,0.4896218953451279,0.4952131142666213,0.5012341794506459,0.50766056247432,0.51446426462305,0.5216139872662083,0.5290752706228414,0.5368105819465973,0.5447793343834761,0.5529378196349399,0.5612390433463013,0.5696324656527224,0.5780636756865204,0.5864740724295726,0.5948006831011521,0.6029763074343156,0.6109301957129122,0.6185894096346389,0.6258808691112544,0.6327339051701941,0.6390830036049415,0.644870392074858,0.6500481883611002,0.6545799415502467,0.6584415123938024,0.6616213259211344,0.6641200807234967,0.6659500194674312,0.6671338636938158,0.667703503465617],[0.4739769042543667,0.4714698125822986,0.46914870704460504,0.4670390629297834,0.46516667930939737,0.46355739210720426,0.4622367557359045,0.4612296979789512,0.46056015462440436,0.4602506921685074,0.4603221285474505,0.46079316315254465,0.46168002815666737,0.4629961732665691,0.46475199530038147,0.46695462242803965,0.469607760548974,0.47271160625268316,0.47626282732602465,0.4802546080910721,0.48467675323023474,0.48951584037886875,0.49475540874223856,0.5003761683052341,0.5063562117110157,0.512671208362009,0.5192945575038792,0.5261974738781515,0.5333489762321407,0.5407157466082719,0.5482618294210588,0.555948148804102,0.563731848724168,0.5715655133467413,0.5793964113781088,0.5871660137743837,0.5948101065054118,0.6022597772939552,0.6094433564986307,0.6162891129765995,0.6227282992651937,0.6286981015424681,0.6341441501306678,0.6390223975715211,0.6433003056956047,0.6469573750226948,0.6499851003353432,0.6523864558274198,0.65417501328023,0.6553737870009263],[0.4758068846686838,0.47326332281472533,0.4708866402073507,0.46870003135268085,0.4667269345980561,0.464990772945017,0.4635146695486031,0.46232114259215684,0.46143178577551536,0.46086694214967105,0.4606453803476177,0.4607839832602758,0.4612974597491155,0.46219808995248185,0.46349551404710854,0.46519657294085465,0.46730520733271397,0.4698224189808259,0.472746295017762,0.4760720929177939,0.4797923804154055,0.48389722141233305,0.4883743957256289,0.49320963735418544,0.49838687260332204,0.5038884356495738,0.5096952346630463,0.5157868362221841,0.522141429528412,0.5287356256072758,0.5355440424545745,0.5425386299529589,0.5496877083407059,0.5569547480519562,0.5642970275273603,0.5716644718616615,0.578999136006479,0.586235800045858,0.5933038685606822,0.6001303233200496,0.606643166621731,0.612774773030802,0.6184647448544316,0.6236620754796719,0.6283265788497093,0.6324296332432193,0.6359543305975881,0.6388951369173098,0.6412571676310126,0.6430551725604923],[0.4776235924200225,0.4750411279825865,0.4726066238630179,0.47034109586140893,0.4682657378468278,0.466401689659048,0.46476978513564027,0.46339028489224654,0.4622825997921396,0.46146501227487635,0.4609544037698359,0.4607659971877403,0.4609131238537483,0.46140702412764734,0.46225669028804783,0.46346875901705215,0.4650474590348402,0.4669946171687857,0.46930972350003963,0.4719900533244257,0.4750308405918219,0.4784254943039844,0.48216584604228585,0.48624241326638956,0.490644659084413,0.495361224577035,0.5003801041483585,0.5056887274842948,0.5112739033953044,0.5171215714204601,0.5232162979541005,0.529540448653919,0.5360729773160149,0.5427878138304882,0.5496519482248912,0.5566235358647169,0.5636506517814942,0.5706714475073111,0.5776160856816231,0.5844100928087042,0.5909783011745119,0.5972486185234602,0.6031551853120467,0.6086407572936423,0.6136583111420896,0.6181719456669315,0.6221571801191922,0.625600757274897,0.6285000541949359,0.6308621940343149],[0.4794267275759639,0.4768039229544308,0.4743105078470337,0.4719654329145075,0.46978777458458887,0.46779652921087744,0.46601039217245943,0.4644475264282199,0.463125326142894,0.4620601820184462,0.4612672558094126,0.4607602720850879,0.4605513355399235,0.460650781974924,0.4610670704292786,0.46180672281498536,0.46287431581287236,0.4642725277706208,0.46600224096628867,0.4680626969322373,0.4704516996258669,0.47316585809942097,0.47620085691921105,0.4795517388030555,0.48321317959644994,0.4871797305361226,0.4914459964465989,0.4960067107617156,0.5008566588013119,0.5059903895188873,0.5114016434840801,0.5170824131534264,0.5230215465080876,0.5292028241677119,0.5356025295963898,0.5421867898458469,0.5489094634223796,0.555711766645879,0.562524346179681,0.5692712151791619,0.5758742769217308,0.5822574809200902,0.5883502047507276,0.5940897794462386,0.5994232097763749,0.6043081865882971,0.6087135001962245,0.6126189621386835,0.6160149352147981,0.6189015620357778],[0.4812169640656278,0.4785533875120766,0.47600112528716587,0.4735771856837257,0.47129866316213787,0.46918255780182017,0.4672455839394843,0.4655039723568571,0.46397327130850813,0.4626681525158232,0.46160222892570785,0.4607878914699313,0.4602361721950387,0.45995664090677946,0.4599573418478073,0.4602447758858952,0.46082393223763907,0.46169837191468766,0.4628703628920903,0.46434106449644913,0.46611075571390426,0.46817909901127885,0.47054542778856184,0.47320904162191885,0.4761694888381373,0.47942681045203217,0.4829817128215167,0.486835628232853,0.49099061273707956,0.4954490187098153,0.5002128657924347,0.505282818615684,0.5106566651765235,0.5163271841735719,0.5222793259553927,0.5284868350699788,0.5349091151286316,0.5414901619687206,0.5481609251644665,0.5548440468408306,0.561458978924449,0.5679264205631349,0.5741718214656869,0.5801279789170681,0.5857368267633399,0.5909505282838949,0.595731983333553,0.600054853636251,0.603903201567956,0.6072708284562849],[0.48299575793648375,0.48029196979982924,0.4776820494371389,0.47518119250021273,0.4728046530797024,0.47056758738455257,0.46848489033555457,0.4665710292580616,0.4648398796368982,0.46330456857963975,0.46197733216417886,0.46086939316334774,0.45999086568780717,0.4593506930216705,0.45895662430984535,0.45881523477375663,0.4589319927804632,0.45931137537885613,0.45995703186072634,0.4608719925150428,0.46205891701633406,0.4635203737909341,0.4652591381692351,0.4672784930447832,0.4695825109624967,0.4721762908457584,0.4750661157094245,0.47825948943919483,0.4817650007981691,0.4855919510323933,0.4897496676414764,0.49424641103964917,0.49908776323963167,0.5042743697783594,0.509798896376386,0.5156421269897307,0.5217687297075208,0.5281252405282137,0.5346429391191801,0.5412435695573397,0.5478449016871331,0.5543652839569276,0.5607271771756631,0.566859779411917,0.5727008611103285,0.5781979245838196,0.5833087947981599,0.5880017402944198,0.5922552145573986,0.5960572994498752],[0.48476516039967965,0.482022677285199,0.4793573611792515,0.4767827295833389,0.4743123416859413,0.4719596651285731,0.4697379389407569,0.4676600366326627,0.46573833408307364,0.46398458741431564,0.4624098264555164,0.461024269611409,0.4598372659294495,0.45885726985349795,0.45809185353737464,0.45754776064668756,0.45723100429299923,0.4571470101182907,0.4573008035791756,0.457697238162932,0.4583412585805613,0.45923818988217285,0.46039403985354094,0.46181579787147475,0.46351170847589834,0.4654914920823818,0.46776647831057466,0.47034960913089713,0.4732552592290821,0.4764988094760505,0.48009589603421154,0.4840612423574729,0.488406964150569,0.4931402183234666,0.4982600463536191,0.5037532437351315,0.5095892867835291,0.5157171487703555,0.5220689089923275,0.5285663166205207,0.5351264832055731,0.5416664269178861,0.5481066020723364,0.5543735434157857,0.5604017448716453,0.5661348835214408,0.5715264911564526,0.5765401674246383,0.5811494203266853,0.5853372116458598],[0.4865276398002192,0.48374887960862956,0.48103143180556474,0.47838727288679006,0.47582841430573863,0.4733667911242549,0.47101414965563704,0.46878193787907085,0.4666812029416122,0.4647225005070238,0.4629158210180003,0.46127053806744595,0.45979538398574504,0.45849845740938955,0.45738726697346815,0.4564688143450384,0.4557497185712204,0.4552363821433779,0.4549351972647002,0.4548527885339212,0.4549962855911344,0.4553736161617236,0.4559938063063055,0.4568672704360337,0.45800606865417326,0.4594241030832563,0.461137217862123,0.4631631592719036,0.46552134280401875,0.46823236276638835,0.471317167120117,0.47479580557570816,0.4786856425309128,0.48299890821880576,0.48773944149544024,0.49289845609284016,0.49844924178510963,0.5043435283703604,0.5105153104967398,0.5168875478492336,0.5233778246105593,0.5299028760981215,0.5363821244983147,0.5427403523772667,0.5489096313867228,0.5548306137356872,0.5604532850117814,0.5657372684564121,0.5706517626502791,0.5751751867090322],[0.4882859158865903,0.48547412684192404,0.4827087247280256,0.4800002828301848,0.47735941167360985,0.474796668306955,0.47232246700616526,0.469946994958253,0.4676801369239044,0.4655314132247039,0.46350993561892856,0.461624385682806,0.4598830201669152,0.4582937074183854,0.4568639983212829,0.4556012342870809,0.45451269360476093,0.453605775917433,0.4528882227084885,0.45236836942765185,0.4520554222267452,0.45195974915139914,0.452093171973702,0.4524692405558329,0.45310346658914813,0.45401348762209476,0.45521912532666836,0.4567422938055622,0.4586067042651052,0.4608373014427972,0.46345935467967064,0.4664971124022546,0.4699719130322928,0.47389962823882975,0.4782872982229159,0.4831288317122625,0.488400080023506,0.4940560742702309,0.500034032646123,0.5062593741564538,0.5126512903497737,0.5191272703365691,0.5256066597143371,0.532013376076252,0.5382778961749191,0.5443386198157305,0.5501427061798665,0.5556464695875913,0.5608154135642825,0.5656239743713605],[0.49004280900941477,0.48720198584098073,0.48439361883881915,0.4816270146534397,0.478911527407928,0.4762564873193778,0.4736711328046545,0.47116454940304375,0.4687456192013016,0.4664229847087938,0.46420503126986357,0.4620998920851039,0.46011547971144484,0.458259547493547,0.4565397837190323,0.4549639403631164,0.4535399970711806,0.4522763594970513,0.45118208924341885,0.4502671604052527,0.44954273505361736,0.44902144685870604,0.4487176783642179,0.44864781310058627,0.4488304386559588,0.4492864708920776,0.45003916256967175,0.4511139516065312,0.4525380949129066,0.45434002314394534,0.4565483397592291,0.45919037467312346,0.4622901894469358,0.4658659216034553,0.46992637113261027,0.47446688121308245,0.47946525479641877,0.4848798910593667,0.49065200862896663,0.4967105601919219,0.5029774218432412,0.5093718478488651,0.5158140456361908,0.5222279388890358,0.5285432198395674,0.5346967906183075,0.540633686116683,0.5463075625859631,0.5516808282036152,0.5567244842766349],[0.49180110616454287,0.4889358965827264,0.48609025535864925,0.4832723561519866,0.4804904371769142,0.47775274782869825,0.4750675005218968,0.47244283083945743,0.46988676936797436,0.46740722878098445,0.46501200980093904,0.4627088295924668,0.46050537588597085,0.4584093896737412,0.4564287786340455,0.45457176249643755,0.45284705033813344,0.4512640482694825,0.4498330940952298,0.44856571329006273,0.4474748879555617,0.44657532727368676,0.44588372426927986,0.44541897935780383,0.4452023660903848,0.44525760861442715,0.4456108335427452,0.4462903510795915,0.4473262113436006,0.44874947192429965,0.4505911021834209,0.45288043992032617,0.4556431107891436,0.4588983334806809,0.4626556069558651,0.4669110275382629,0.4716440782535625,0.47681637636739155,0.4823733577409551,0.48824817310028834,0.49436625249763866,0.5006495261405584,0.5070199497629808,0.5134022937821532,0.5197262554343667,0.5259279775047461,0.5319510587802395,0.5377471362777791,0.5432761125062822,0.5485060939927394],[0.4935634451250055,0.49067904963177245,0.48780240918666823,0.48494069363962317,0.4821011601988967,0.4792911166969145,0.47651789148224283,0.473788812798388,0.4711112007167515,0.46849237480946276,0.4659396807522233,0.4634605389112335,0.46106251766499556,0.45875343371472993,0.45654148091995983,0.4544353882320374,0.4524446060606042,0.4505795188665057,0.44885167989598285,0.44727406171571005,0.445861313529659,0.44463001310126815,0.4435988974032629,0.44278905180004224,0.44222403255685494,0.44192989169293156,0.441935066599412,0.4422700894290343,0.4429670631657639,0.44405884294246517,0.4455778537961695,0.44755447274542437,0.4500149117992597,0.4529785789523699,0.45645500963515756,0.4604407171323063,0.46491670328336204,0.46984760170261275,0.47518299603973213,0.4808605097247843,0.486809692206319,0.49295586734307817,0.49922350995366616,0.5055390081288528,0.5118328100459697,0.5180410087335856,0.5241064350766247,0.5299793312977431,0.5356176735434572,0.5409872066765791],[0.49533221728879284,0.492434285200589,0.48953338501401644,0.4866358061568105,0.48374795280407845,0.48087632238978123,0.4780274918677052,0.4752081143394104,0.4724249288102586,0.4696847858908265,0.46699469220624057,0.4643618760856502,0.4617938767530343,0.4592986587031675,0.4568847521968659,0.45456141982065856,0.4523388477994937,0.45022835919612,0.4482426442429871,0.44639600079262304,0.4447045751956673,0.44318659077150857,0.4418625473698312,0.44075537127678477,0.43989048984896745,0.4392957997382166,0.43900149143375833,0.43903968625363926,0.439443835288518,0.44024782413092567,0.4414847247273694,0.4431851411765191,0.4453751197641601,0.4480736538355894,0.4512899390923359,0.45502074068274556,0.4592484596279786,0.46394053654292494,0.46905051144536897,0.4745204990656503,0.4802844518544742,0.4862715741347892,0.49240946496955934,0.4986267885612722,0.5048554146952419,0.5110320456466604,0.5170993781926652,0.5230068605835634,0.5287111057986391,0.5341760196033225],[0.4971094893140682,0.4942040136573317,0.4912859377941363,0.488360787208246,0.48543423297823973,0.4825120841203612,0.4796002885331751,0.4767049449144912,0.47383232810696135,0.4709889303279364,0.4681815206297045,0.4654172246951874,0.46270362667764064,0.46004889421623685,0.4574619269770392,0.4549525280540684,0.45253159628957734,0.45021133600558233,0.44800547874669305,0.44592950938051146,0.4440008862466387,0.44223924194744685,0.4406665477943302,0.43930722083336154,0.43818814777019394,0.4373385950449315,0.4367899689290669,0.43657538419155506,0.4367289953741751,0.4372850425589903,0.4382765666639835,0.4397337632337264,0.44168197767368045,0.4441394120391223,0.4471147249875769,0.45060485224838526,0.45459349366933005,0.4590506930769493,0.4639337080106466,0.46918901720857986,0.4747550499487081,0.48056516497789314,0.4865505104430409,0.4926425460963406,0.4987751318649288,0.5048861649145497,0.5109187895471174,0.5168222240168396,0.5225522556071142,0.5280714560941377],[0.4988969431266768,0.49599015680508735,0.493062216585513,0.4901179926844571,0.4871625341225439,0.4842010734727882,0.4812390408115039,0.4782820889924752,0.47533613239808475,0.47240740126786174,0.46950251354504446,0.4666285658936193,0.4637932450992733,0.4610049604541353,0.4582729969123442,0.45560768776547944,0.4530206042963439,0.450524758297498,0.4481348114567304,0.4458672833836935,0.4437407474492462,0.44177600060480415,0.43999618992733497,0.4384268748041039,0.43709599948324757,0.4360337463102177,0.4352722356394314,0.434845034724337,0.4347864358994411,0.43513046594345556,0.4359095968211152,0.43715314802296723,0.43888540925565417,0.44112357592692564,0.443875678790341,0.4471387848906708,0.45089780340057284,0.45512518753509174,0.4597816595688509,0.4648178579748056,0.470176623000586,0.47579557227531477,0.48160966175526576,0.48755352214636827,0.49356345578856553,0.49957905040407025,0.5055444115631611,0.5114090411587018,0.5171284015245372,0.5226642093672824],[0.5006958334710465,0.49779410881012776,0.49486373030189307,0.49190901310462964,0.4889344857060427,0.48594490565038106,0.48294528483719823,0.4799409262611718,0.4769374740470106,0.4739409785323427,0.4709579779455296,0.4679955978943176,0.46506166940375326,0.46216486559544195,0.45931485626163715,0.4565224785324702,0.4537999205376498,0.45116091339939796,0.44862092503572015,0.4461973470786218,0.44390966370196233,0.44177958830039255,0.4398311507771092,0.43809071473449956,0.43658690023464386,0.4353503842353746,0.43441354772990837,0.4338099367493345,0.4335735049363716,0.4337376102895221,0.4343337507703863,0.43539004655697683,0.4369295147761595,0.4389682372888991,0.44151358829504544,0.444562748323751,0.44810175363899646,0.45210528443762604,0.4565372765714517,0.46135228702880654,0.46649741436397224,0.47191451588796235,0.4775424763536041,0.4833193400232231,0.4891841868474842,0.495078693288986,0.5009483617445245,0.506743430295631,0.5124194903545475,0.5179378475265346],[0.5025069618370068,0.49961671529705176,0.4966913335238974,0.49373466791492115,0.49075081806220955,0.48774415704416835,0.48471936644623836,0.4816814827294006,0.4786359565056627,0.4755887261352084,0.47254630681259224,0.4695158959403252,0.4665054950774935,0.46352404807785397,0.46058159417466493,0.4576894337063819,0.4548603028863818,0.4521085524800591,0.44945032344543245,0.4469037105054728,0.4444889022482726,0.4422282837090866,0.44014648452055044,0.4382703527185129,0.436628831336874,0.4352527123206794,0.43417424053691983,0.43342654056747165,0.4330428417427072,0.43305548425047985,0.43349470338003465,0.4343872124677257,0.43575463952947835,0.43761191671898125,0.43996576886062,0.4428134830345551,0.446142145952044,0.4499284941007802,0.4541394347835983,0.4587331882402591,0.4636609081208517,0.46886858726996633,0.4742990537506424,0.4798938949347552,0.48559519548337293,0.4913470223388646,0.49709662821962636,0.5027953724495665,0.5083993754781686,0.5138699334787754]],"zauto":true,"type":"contour"},{"autocolorscale":false,"autocontour":true,"colorbar":{"len":0.875,"tickfont":{"size":8},"ticksuffix":"","x":1,"y":0.5},"colorscale":[[0.0,"rgb(255,247,251)"],[0.14285714285714285,"rgb(236,231,242)"],[0.2857142857142857,"rgb(208,209,230)"],[0.42857142857142855,"rgb(166,189,219)"],[0.5714285714285714,"rgb(116,169,207)"],[0.7142857142857143,"rgb(54,144,192)"],[0.8571428571428571,"rgb(5,112,176)"],[1.0,"rgb(3,78,123)"]],"contours":{"coloring":"heatmap"},"hoverinfo":"x+y+z","ncontours":25,"visible":true,"x":[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],"xaxis":"x2","y":[1e-06,1.757510624854793e-06,3.0888435964774785e-06,5.428675439323859e-06,9.540954763499944e-06,1.67683293681101e-05,2.94705170255181e-05,5.1794746792312125e-05,9.102981779915228e-05,0.00015998587196060574,0.0002811768697974231,0.0004941713361323833,0.000868511373751352,0.0015264179671752333,0.0026826957952797246,0.004714866363457394,0.008286427728546842,0.014563484775012445,0.025595479226995333,0.04498432668969444,0.07906043210907701,0.1389495494373136,0.244205309454865,0.42919342601287785,0.7543120063354607,1.325711365590108,2.329951810515372,4.094915062380427,7.196856730011514,12.648552168552959,22.229964825261955,39.06939937054613,68.66488450042998,120.67926406393264,212.09508879201925,372.7593720314938,655.1285568595496,1151.3953993264481,2023.5896477251556,3556.4803062231213,6250.551925273976,10985.411419875572,19306.977288832455,33932.217718953296,59636.23316594637,104811.3134154683,184206.99693267164,323745.754281764,568986.6029018281,1000000.0],"yaxis":"y2","z":[[0.13543102397796292,0.13182603445674745,0.12812197173835244,0.12434568413701097,0.12052925351786013,0.11670991868715876,0.1129296282105822,0.1092340873455703,0.10567116109375391,0.10228852446470435,0.0991305300117428,0.09623440418266534,0.09362608152160964,0.0913161991197428,0.08929692626649587,0.08754030600638467,0.08599858271541161,0.08460661461447391,0.08328604403604985,0.08195057550609358,0.08051159520716787,0.07888345854795391,0.07698799675036101,0.07475804577629967,0.07214000564545885,0.06909556460579709,0.06560277601964523,0.06165667858672044,0.057269627142846745,0.05247147162198661,0.04730970114761551,0.04184967444334851,0.036175115102816145,0.03038923266538092,0.02461735304625031,0.019013534730659164,0.013779126829844493,0.009222295122745723,0.00595129958946789,0.004968382191747059,0.005836202839849086,0.006795962623470127,0.0070463875127331965,0.006465466723469471,0.00540355921313035,0.005085102180396452,0.0070486224673486034,0.010887690164101455,0.01575568515594681,0.021257955207103583],[0.1328460340392906,0.12896816257381563,0.12497211545285596,0.12088615988019882,0.11674487617697367,0.11258937078215366,0.10846712725420521,0.10443131277813997,0.10053932506709118,0.09685036312610938,0.09342186824049618,0.09030484533861619,0.08753835761711239,0.08514385336549386,0.08312031592692752,0.08144134580863532,0.08005503913902762,0.0788869276058011,0.07784550629002758,0.07682930972986737,0.07573431676566501,0.07446066832667868,0.07291809656276894,0.07102988533475481,0.06873548403322816,0.06599204928061957,0.0627752242480974,0.059079433247529616,0.0549179125320577,0.0503226450921627,0.045344336112868665,0.04005257620648066,0.03453643274650365,0.02890600061686533,0.02329628898619588,0.017877438045505123,0.012884181479303142,0.008707973278707959,0.0061202541397840995,0.005904597428726382,0.007061262388317721,0.008110446674299134,0.008454582470320765,0.007993098299561562,0.006961218198697221,0.006134438580157628,0.006913272869716234,0.009798281173295372,0.014076597621850834,0.019189387499807493],[0.1303110772317582,0.12615375201067258,0.12185581001427863,0.11744621868205136,0.11296132739976139,0.10844545572879563,0.10395117810851896,0.09953908258111885,0.09527670347697938,0.09123626653775335,0.08749088878318964,0.08410902007798358,0.08114727638323815,0.07864240840967676,0.07660382687785212,0.07500852703533713,0.07380003605421372,0.07289203572352056,0.0721759647150155,0.07153085130024678,0.07083334568805867,0.06996637978332426,0.06882567705237957,0.06732404921776697,0.06539384631946332,0.06298807766212851,0.06008069439823944,0.056666422929022874,0.052760429994676006,0.04839802058983533,0.043634538152931224,0.03854567822031275,0.03322860766138673,0.027804791822043463,0.02242683905861966,0.01729570989248504,0.012705973513852505,0.009154109919770833,0.007398393037647159,0.007661098449875821,0.008852540120648681,0.009902302383707897,0.010344673816581008,0.010081407502686636,0.00926891173464772,0.008380285796117354,0.00830804067603572,0.009915812529758252,0.01319463330348908,0.017646364848904427],[0.12786243541798703,0.12342342004041733,0.11881811149887636,0.11407525161641632,0.10923192300562341,0.1043345814588668,0.09943990999164032,0.0946152583314771,0.08993829921602575,0.08549537679031764,0.08137789585132678,0.07767612431712843,0.07447014458814855,0.0718185617028658,0.06974687904455351,0.06823861537506908,0.06723231732941577,0.06662605047079323,0.0662883414830747,0.0660724403127979,0.06583033299731303,0.06542401818669104,0.06473314747459283,0.06365933881447683,0.062128025158552175,0.06008875379121742,0.05751466898252428,0.054401681518795215,0.0507676442622313,0.04665174220723164,0.04211427766988092,0.0372371102227997,0.03212528021322987,0.02691104990577717,0.021763426461588478,0.016910954662934668,0.012695310110800242,0.009662098195784749,0.008450991218526932,0.008969411095268831,0.010203982846410284,0.011298698510499057,0.011859891022355344,0.011784164409379069,0.01116473649150317,0.010304086022610447,0.009788365696110874,0.010413604018506805,0.012652495782756387,0.016336034936180913],[0.12553968487819647,0.12082221264611173,0.11590993997908891,0.11083028908844716,0.10561974715870802,0.10032536834658617,0.09500629564826424,0.08973510409773854,0.08459858870079211,0.07969734991494781,0.07514318519629422,0.07105300692136196,0.06753810979368688,0.06468863602735957,0.06255538131108782,0.06113396884225503,0.060357731802376774,0.0601032360714367,0.06020696341618416,0.06048710045632815,0.06076375294368101,0.06087362067583654,0.06067845938973011,0.060068634681615815,0.058963581690657706,0.05731068192983232,0.05508355565056675,0.05228033682762809,0.04892222188703546,0.04505244846237218,0.04073584420248866,0.03605919899626947,0.031133046536145063,0.026096269783790916,0.02112702327652574,0.016468531098757375,0.012486701178817049,0.009748515174524958,0.008832249604579743,0.00952314589755021,0.010846529272808126,0.012036113131693399,0.012733471189013662,0.012827145284051255,0.01236193105615922,0.011533395502845517,0.010748961013970174,0.010682199078395186,0.012030709416628026,0.01498541773872388],[0.12338478268080952,0.11839866885669774,0.11318720004017488,0.10777530732725135,0.10219734429625252,0.09649900971649557,0.09073954379630057,0.0849941098099154,0.07935609468670407,0.07393871277991453,0.06887469391652774,0.06431198724151821,0.06040267504671644,0.05728275400248424,0.05504378792376747,0.053703999366739336,0.05319191276464885,0.05335280713066109,0.053976115788569326,0.054830872768436754,0.05569576833469503,0.05637771976314976,0.05671986263397222,0.056602698363307245,0.05594188244515955,0.05468489643627999,0.052807752496473404,0.05031220310425508,0.04722359315252801,0.04358937108462107,0.03947829240351801,0.03498049444155408,0.030208985287320085,0.025303968344180666,0.020443650565671146,0.01587083941414812,0.011955314984187015,0.009287404916654574,0.008486255730865836,0.009317846863288506,0.01077010428692013,0.012087627764553561,0.012926552405912338,0.013169058414080951,0.012824575131869862,0.012015465987591149,0.011032772787388383,0.010447201723744946,0.011070808401046992,0.013414961855503083],[0.12144076926028123,0.11620337427430423,0.1107092357068901,0.10497969466736098,0.09904540114412974,0.09294851209693679,0.08674541914337466,0.0805100969087768,0.0743380710395664,0.06835071542937078,0.06269886944897922,0.05756327459456967,0.05314691633709053,0.049652200441523464,0.047238327163321055,0.04596713715397284,0.045764680480453505,0.04642722818012143,0.04767090372764377,0.049193836600184865,0.050721611440559304,0.05202839560509404,0.052940767234947055,0.053333356814275375,0.053122174493188304,0.05225829983301999,0.05072278378138253,0.048522822567368756,0.04568900990654682,0.042273454563867496,0.0383486365822746,0.03400705180013021,0.029362050110295437,0.024551102459065017,0.019744911712637557,0.015171919363887369,0.011183482031326922,0.008387063380257279,0.0075429496192692975,0.008488202109114424,0.01008743149224813,0.011538119694010756,0.012504151736017136,0.01286815473555999,0.012615592923913666,0.011814319451144924,0.01066801491162144,0.009661517198382399,0.009689474544686365,0.011575997027978353],[0.11975008997213153,0.1142869725982889,0.1085365254838916,0.10251567475176084,0.09625004236876962,0.08977618524184816,0.0831445377822445,0.07642334486737247,0.06970395749981557,0.06310786229099424,0.05679544344150319,0.050974971492821944,0.04590612703146663,0.04188411104770633,0.03918312341097095,0.03795403621838803,0.03812865707672313,0.03941832500928206,0.04141645186743421,0.043717188654179055,0.04598197808438234,0.047954918666391996,0.049453725910734644,0.05035507060621059,0.050581704211515456,0.05009292477882185,0.048877966346434765,0.04695152620618586,0.044350755141149195,0.041133232460282707,0.03737563653709686,0.033173021979481764,0.028638922672091914,0.023907173458015185,0.019138162707793394,0.014537853699660855,0.010416377343770683,0.0073534717498653845,0.006292531284638595,0.0072814690728063534,0.00899457429562775,0.010538007745877275,0.011587523911124279,0.012035698219181547,0.011852805137183826,0.01106161520382555,0.009789085331582263,0.008435043844551359,0.007970270434727098,0.00957947236441546],[0.11835259510343855,0.1126976796748466,0.10672761809904008,0.10045458871584942,0.09389844749172122,0.08708874051965751,0.08006743046076496,0.07289273940932468,0.06564478421730625,0.05843411661768658,0.05141484829773107,0.04480421146923519,0.038907646791657965,0.03413473929655698,0.030954702278430522,0.029714492148482992,0.030379718957894035,0.03249216662492722,0.035423059092376585,0.03861865930933375,0.04167727344462808,0.04432964336662024,0.046401297160342934,0.0477831845577247,0.048412748638347575,0.04826237085439056,0.047332362360984995,0.04564665450057087,0.043250080974026425,0.040206599617502684,0.036598079275729084,0.032523481225753326,0.02809850656277908,0.023456266544932287,0.018750847261659476,0.014169875151203529,0.00997782123221615,0.00666679470410732,0.00523080925195833,0.006066548169173196,0.0077496263791834745,0.009274091833597115,0.01032623982288632,0.010812108491786569,0.01069019007778857,0.0099415274476621,0.008619663222576849,0.00703042852000561,0.006205623717099531,0.00775559524394507],[0.11728334771869588,0.11147844922360137,0.10533546214206128,0.09886215079006792,0.09207276654822333,0.08498963446803116,0.07764528480811532,0.07008548755724449,0.06237387750552791,0.05459954436004147,0.046890423944294365,0.039438365474710156,0.032547003288767765,0.02671438635436538,0.022706278357253022,0.021338468527866018,0.022716890491765375,0.025971213774425746,0.03004807421117256,0.034223686356197526,0.03807702481746728,0.04136618576196078,0.04394973307835073,0.04574647851880284,0.04671535285936001,0.04684501090149352,0.04614822574350506,0.04465873294506,0.0424293740146217,0.03953094073036889,0.036051396096517446,0.032095316673366944,0.02778358031789849,0.02325367643995715,0.0186619689388458,0.014192248548832142,0.010085600313280757,0.0067440425073242724,0.0049602572559063795,0.005292074239059357,0.006632955707062078,0.007939551490109251,0.008877534607749541,0.009353630737347012,0.009310152939188476,0.00868698977915742,0.007475424193785687,0.005905275192229569,0.005031588439195971,0.00671183098492236],[0.11657043848881896,0.11066405517417298,0.10440347340031388,0.09779310067954607,0.09084279747398133,0.08356901171569273,0.07599620350075009,0.06815874565549702,0.0601036870608703,0.051895245538901326,0.04362314022025233,0.03542041847117773,0.0275076328816521,0.020317864445259716,0.014851753038980184,0.013054716811309076,0.015662086121151535,0.020525008042214788,0.025878166889638975,0.03097860602442911,0.03550596763081214,0.039299356211709026,0.04227039266168936,0.04437191402487404,0.04558521114378971,0.0459142402554408,0.04538278637443305,0.044033009452296705,0.04192469012611809,0.03913484396075787,0.03575753137610097,0.03190378802409385,0.027701719009896708,0.023297055521405277,0.018855149456690562,0.014567319347145863,0.010670068402249903,0.007497933782024396,0.005556461400247382,0.005200118069957212,0.005854192217104838,0.006702268003358634,0.00739740152095898,0.007834053237306628,0.007928465430609299,0.007576993612582246,0.006734187275667918,0.005621996147198498,0.00521706146672146,0.006974477308331948],[0.11623305601599467,0.11027844918712824,0.10396185953692035,0.0972860041197329,0.09025849536691481,0.08289270791080372,0.07520876328356477,0.06723467532377313,0.05900775010473119,0.0505764658860288,0.042003433853538254,0.033371266088534614,0.024798027060395342,0.01649434492598119,0.009096226910202027,0.006132008844341721,0.010931963395627412,0.01744011751107685,0.02371547019880835,0.029377423984510976,0.03427837361562193,0.03833748052721813,0.041506956940942356,0.04376217700416295,0.04509800681595007,0.045527240701443226,0.045079917125415855,0.04380307429004012,0.04176075880497698,0.039034193773016534,0.035722054609612704,0.0319408347494408,0.02782534077439497,0.023529486865257847,0.019227862504080366,0.015119192036638486,0.011433620314651716,0.008442411028140816,0.006434215063614657,0.005530459077172545,0.0054327912823900724,0.005684246593232968,0.006056927375159563,0.006472421924969151,0.006810334299589292,0.0069024382717128826,0.0066671364034580445,0.006306849037409241,0.006530378194242676,0.008236517699493021],[0.11628006861035554,0.11033278284047605,0.10402480628246072,0.09735915707172903,0.09034385211216275,0.08299282499998965,0.07532699584848125,0.06737556536850883,0.059177689605350026,0.0507849042884807,0.042265261372808206,0.03371203142843927,0.02526701674527965,0.01720328460198652,0.010334212888807443,0.00784522185305813,0.011961498415007026,0.018087258927220375,0.024180668887276154,0.02974108386682065,0.03457887351056506,0.038596057366876164,0.04173672565532617,0.04397197078909465,0.04529425449471669,0.04571501673722886,0.045263628617599534,0.04398700395986378,0.041949584662157945,0.03923356325389796,0.03593926677152707,0.03218565491472855,0.028110903777648206,0.023873056906764504,0.019650686419677127,0.01564318200686367,0.01206860416614789,0.009150112645214696,0.007063353149626608,0.005818230727749677,0.005198234529667491,0.004967262551336774,0.005087895779696565,0.00557455847001028,0.006249739162111238,0.006841693248775651,0.007206960714597885,0.007473570485700221,0.008112797947564513,0.009749590507182696],[0.11670932564003737,0.11082442230998221,0.1045890561578576,0.09800848087384882,0.0910936811088687,0.08386263625397235,0.07634195338414175,0.06856911551251796,0.060595848354898736,0.052493703222817746,0.04436442664483111,0.036361608090116876,0.028741084302197187,0.021986295218835484,0.017077691459489473,0.015531300980455237,0.017750744850972385,0.022124272039815637,0.027127971849029854,0.03199616342682833,0.03636643725215412,0.04005092175802992,0.0429454095887991,0.04499332914035118,0.04617027496222536,0.04647681922441533,0.04593499128764267,0.04458654474357258,0.04249217561758691,0.03973128284842637,0.03640204541419941,0.03262166753238117,0.028526664967576085,0.02427303795666588,0.020036047602706067,0.016008856319971627,0.012397680283964707,0.009405854733460357,0.007187648104233075,0.0057585359002274425,0.0049562127247053025,0.004618938794267171,0.004776564736017735,0.005453489998787314,0.006408248763584275,0.0073211970291124345,0.008028146305698224,0.008610794584367133,0.009424503605479948,0.010982400454642258],[0.11750778705215086,0.11173712989615128,0.10563416896272422,0.09920790644590098,0.0924742025322246,0.08545751264822607,0.07819324413378695,0.07073112917785108,0.06314035249489476,0.05551784509216469,0.048002463760465304,0.04080007415206757,0.034226922572420465,0.02877108608123871,0.025110640102461435,0.023874980299027425,0.025087876470575143,0.028029785307123804,0.03180108871771939,0.035730115230509576,0.039396848748604905,0.042548186642922675,0.04503166660784697,0.04675765326967708,0.04767910553269537,0.047780709109324145,0.04707292440213918,0.045588683430025354,0.0433815665947257,0.040524825007384205,0.03711087263830543,0.03325099339308097,0.029075058860828944,0.024731071405260582,0.020384369243367353,0.016216395786994468,0.012422989512257107,0.0092111959503611,0.006785716823219487,0.0052884557531144944,0.004671294123519993,0.004711465106543754,0.0052372467202136085,0.006122037868699601,0.0071509708131607536,0.008089816662775915,0.008818214156088968,0.009414592434690722,0.010195733216742338,0.011638978086997077],[0.11865246119565155,0.1130423802835269,0.10712441044772174,0.10091215480548943,0.09442726158807599,0.08770155225623326,0.08077989566038883,0.07372422244486765,0.06661930780626393,0.05958127183365436,0.05277000773829186,0.04640619868948097,0.040789603771795295,0.036301649329081115,0.03334859860707485,0.03220008482278216,0.03279576122825896,0.0347297811240037,0.037448152558288574,0.040445296484846675,0.04333852242596752,0.04586176819136881,0.047837683106019234,0.049152815190034845,0.049740421598130385,0.04956948912354272,0.048637901395988406,0.04696820982579936,0.04460500556225453,0.041613254238408524,0.038077170367530305,0.03409932810032436,0.029799779184802828,0.025315037416440946,0.020797013681006105,0.016412673862115652,0.012347286919177297,0.008820071241223325,0.006130709938697636,0.004689305403031583,0.004620758351634657,0.005337705428754651,0.0062982063311652755,0.007294698092984393,0.008207335745412195,0.008922891515195243,0.00939549804452215,0.0097382132642783,0.010290454816609116,0.01156007103035543],[0.1201120081207192,0.11470158309486211,0.10901189220961935,0.10306126929949604,0.096877031653767,0.09049776958545222,0.08397632300688333,0.07738369013407338,0.07081414542726792,0.06439173658929503,0.05827777709532616,0.052677250308729495,0.047838058906065434,0.0440306038143418,0.04149232563115426,0.04033980216274907,0.04049535842819425,0.041692556085751786,0.04356188367988223,0.04572947517600141,0.047876219728458305,0.04975509680384209,0.05118632726949362,0.05204590780677841,0.0522545848196009,0.05176926228206468,0.05057684184218218,0.04868995708815115,0.04614404118524971,0.042995271145245914,0.03931903893396793,0.03520868800774315,0.030774347010534376,0.02614186050042037,0.021452246049282683,0.01686335293440952,0.012559320127598217,0.008786505796766824,0.005967707219463831,0.004807957323233697,0.005377351968991667,0.006602513965853307,0.007796228890818387,0.008756959025854376,0.009416356489941791,0.009733581240884751,0.00972616446933776,0.009562785998355233,0.009668598160016839,0.01068132760552412],[0.1218487802406164,0.11666885546655106,0.11124039188166286,0.1055859584653926,0.09973760277327678,0.09373903574420789,0.08764829946019094,0.08154096172167827,0.07551375392929408,0.06968823296481859,0.06421330102416684,0.05926402011326241,0.055032186717081884,0.05170296368133084,0.04941524066325311,0.04821499230536193,0.04802504258836325,0.048653013478396914,0.04983488159566307,0.05128877217912557,0.0527553945332112,0.05401822639416753,0.05490849924684682,0.05530238899360771,0.055115566156429964,0.05429766996125301,0.05282764719268242,0.05071012073196001,0.0479726550536566,0.04466370879187853,0.04085108032721982,0.03662071954943431,0.03207591696165823,0.027337188450936717,0.02254393180588863,0.017860956829902703,0.013498710073103484,0.009770709097200505,0.0072123223513531984,0.006459857490293381,0.007251995764693218,0.00854671011962753,0.009700183850223382,0.010474142906714203,0.01078160420632442,0.010591440229262138,0.00994087578845672,0.009031462734359225,0.008415567248980776,0.009043668259446289],[0.12382104180024961,0.11889395657866576,0.11374926197446567,0.10841283443372383,0.10292002458328897,0.09731752484000258,0.09166545825263216,0.08603956712870811,0.08053319053139522,0.0752583706009422,0.07034486471886668,0.0659351216237299,0.06217280489370329,0.05918321313475995,0.057047234156333726,0.05577608376764512,0.05529810643387206,0.055465699600502585,0.05608015028579563,0.05692334354990724,0.05778499053664069,0.05848001116895563,0.05885655549767272,0.058797709794130584,0.058219904708083026,0.05707006828071284,0.05532262823484066,0.05297684933161694,0.05005466017580785,0.046598982207390935,0.042672551441156906,0.03835729814158171,0.03375455547378492,0.02898683012380983,0.024202892328075605,0.01959016208641366,0.015402236724592854,0.012007383193698531,0.009896019028675804,0.009372685304978506,0.010039966373636718,0.011112464228384975,0.012028623338926105,0.012506646188436835,0.012413564136756513,0.011690059476769807,0.0103465758475843,0.008545023698765938,0.006887585101820812,0.006902620279782382],[0.125985130720521,0.12132505002864377,0.11647695615973605,0.11146889030050326,0.10633791786211895,0.1011315610950374,0.09590921113326822,0.09074330631603547,0.08571988937006378,0.08093790315256423,0.07650628438793476,0.0725377056049821,0.06913801267903465,0.06639145619896962,0.06434392574566351,0.06298883967102009,0.06226123178213843,0.062043253182265126,0.06217959319185307,0.06249746195672411,0.06282526699563712,0.06300642043862928,0.06290755412991496,0.062422197506227434,0.06147149664924416,0.0600033428649291,0.05799084813179123,0.05543072188902372,0.05234184944251146,0.048764244048830556,0.044758524948781374,0.040406162547899374,0.03581096436835102,0.031102728259197795,0.026444729969858492,0.02204736072505923,0.01818764718571152,0.015214873708660752,0.013463663961078075,0.012996638888057965,0.01343135047189173,0.014182846582352478,0.014776824612841175,0.014919195282129743,0.014443456835607153,0.013261667212557969,0.01135221036607682,0.00880812305469421,0.006104589372076159,0.005225526326744479],[0.12829738414250244,0.12391106425829998,0.11936388913283606,0.1146848942271304,0.10991135874388987,0.10508977697520962,0.10027662987411076,0.09553872034286831,0.09095271165841798,0.0866033688467111,0.08257990211075054,0.07896986419149729,0.07585042819603025,0.07327770174923162,0.07127591237177507,0.06982929385951635,0.06887949537542674,0.06832987738610131,0.0680557275936873,0.06791756833134999,0.06777432411651664,0.06749405447952851,0.06696136548171988,0.06608171882722559,0.06478339323492487,0.06301793643886514,0.060759804454753215,0.05800569093613693,0.05477389274609579,0.05110397083466523,0.047056956913596355,0.04271643073071349,0.038190948790881286,0.0336184861826172,0.0291734346368626,0.025074988949726686,0.021588615763417297,0.018994141196674197,0.017479916054681244,0.01698971277266361,0.017188739730976024,0.017623588628506687,0.01789726902564999,0.01773077885453569,0.016950441091320823,0.015464142613240504,0.01325808178392955,0.010446044115036017,0.007510956201387788,0.006216355342514625],[0.13071572039189203,0.1266035360778866,0.12235452871812644,0.11799766172256124,0.11356916206249552,0.10911306948529549,0.10468147913027635,0.1003342623468986,0.09613797972557629,0.09216364787743435,0.08848303381350421,0.08516329679388894,0.08226014448529977,0.07981022220902116,0.07782407023556319,0.07628135572226687,0.07512987322910299,0.07428891841280466,0.0736564105247927,0.0731181684322616,0.07255746313095339,0.07186336324104249,0.07093710790698952,0.06969640734494736,0.06807799016265267,0.06603888203524716,0.06355689901753911,0.06063076545390586,0.05728018696094737,0.05354615773030225,0.04949176961043784,0.0452038070068031,0.04079539870896373,0.036409763079634484,0.03222407689317473,0.028449451043532623,0.02531627356280954,0.02302673179051634,0.021667960041622962,0.02113285217972622,0.021132243983650392,0.021301442930301815,0.021308471358097696,0.020904777190104813,0.01993206287748809,0.018318984304160634,0.016094782946659805,0.013454928786944946,0.010963585305697316,0.009922927318679562],[0.13320083664617796,0.1293579188287185,0.12539875407357437,0.12135134551457964,0.11724989681603899,0.11313501344360335,0.10905355278882993,0.10505795001936437,0.1012048172622272,0.09755261434990048,0.09415825031137025,0.0910726291606641,0.08833541701824058,0.08596964696928833,0.083977086389725,0.08233540537299631,0.08099796751969571,0.07989651882880298,0.07894636611676667,0.07805309692563252,0.07711970135176234,0.07605312306251791,0.07476964290870595,0.07319889765409356,0.07128663528962285,0.06899647268772323,0.06631097645155237,0.06323237939456033,0.05978321278746499,0.056007100992850424,0.051969930922177145,0.047761540296934205,0.04349786334911495,0.03932288314276721,0.03540827874981362,0.031945739102904526,0.029123211914751635,0.027077469604918847,0.025832420042406858,0.025261820454024652,0.025114595512415138,0.025089678412794136,0.02490952223924288,0.024362073943288765,0.02331683517005764,0.021734658650015115,0.01969139920622098,0.017438153082271427,0.015516956972156007,0.0148340453724522],[0.13571703255603726,0.1321344020551923,0.12845259089211078,0.12469795857283844,0.12090200843963902,0.11710132589254359,0.11333716562121411,0.10965456087256838,0.10610082531822132,0.10272334482870268,0.09956662900338449,0.09666872245151596,0.09405725838679908,0.09174563668022209,0.08972995612816784,0.08798734337364791,0.08647614577575098,0.08513811519997044,0.0839023106446779,0.08269013212121464,0.08142076832808731,0.08001640956062135,0.07840677921100184,0.07653277784583412,0.07434923909186517,0.07182693302866554,0.06895402164102764,0.0657371903583169,0.06220266885820796,0.058397321469659126,0.05438991984662042,0.050272557683878026,0.04616181250018282,0.04219849017399475,0.03854335059257178,0.03536424379223055,0.032809346943372356,0.030966238512883448,0.029820650419923326,0.029241570193742007,0.02900898711195303,0.028869827643181,0.02859202140541842,0.027999904567773813,0.026993767830984425,0.02556534534552705,0.023821570871828603,0.02202492690981442,0.020638916395339307,0.02029960201008541],[0.13823270231556492,0.13489832383957534,0.13147846289947437,0.1279973515499889,0.12448337469346187,0.12096882538208821,0.1174893367016422,0.11408290452005057,0.11078842749562444,0.10764372646835389,0.10468307208380624,0.10193434850647881,0.09941610132574462,0.09713483157174736,0.0950829637361711,0.09323789269625173,0.09156238374309314,0.09000638318058322,0.08851005495900877,0.08700766645475284,0.08543185790223554,0.08371785591509813,0.08180730214323266,0.07965151454652288,0.07721413705508692,0.07447323771397829,0.07142297852629433,0.06807500592525863,0.06445970417040371,0.0606274114410051,0.056649596983584044,0.052619780903246226,0.04865354339079303,0.04488618799844464,0.04146549037015081,0.038536064549356465,0.036213078245000155,0.0345489870118027,0.033506707529770696,0.03295671431374556,0.03270410584178986,0.032532930123560413,0.03224852972464826,0.03170774471681864,0.030838476863324246,0.029655492586939235,0.02827857965746712,0.026952948692920694,0.026055573914007507,0.02604414637522392],[0.14072055323364044,0.13762026723665902,0.13444509549479194,0.13121683478080393,0.12796054305266452,0.12470417948895712,0.12147796244847904,0.11831339256237329,0.11524190647452127,0.11229316221997199,0.10949301202540715,0.1068612894664077,0.10440961463589059,0.10213948405377486,0.10004093754568257,0.09809206225340746,0.09625949913270593,0.09449997630514265,0.0927627419008891,0.09099264769337377,0.08913357384996597,0.08713189234992734,0.08493972818637993,0.08251786741547346,0.07983825324898502,0.07688608713644289,0.07366160184810097,0.07018159456251205,0.06648079624623922,0.0626130976055681,0.05865252309933475,0.0546935892944758,0.05085022777114029,0.04725175637097446,0.044033628884107515,0.04132065199143709,0.03920256665604778,0.03770743030216445,0.036784472798815776,0.036307856634630105,0.03610248485270089,0.03598098642001262,0.0357784778200584,0.03537837223500774,0.03472997544891293,0.033861680658939484,0.032892117146832336,0.03203623957789164,0.031594141874023145,0.03190283208065473],[0.14315761211873393,0.14027592730900101,0.13732718762711915,0.13433059150491308,0.13130782041682168,0.12828261645065633,0.12528012355570897,0.12232596400282905,0.11944504109552173,0.11666009026158294,0.11399004292042149,0.11144831689202275,0.10904119494534094,0.1067664868030511,0.10461267599918016,0.102558721986274,0.1005746197062877,0.09862272523243523,0.09665975821239381,0.0946393131280585,0.09251466904987789,0.09024168702783918,0.0877816189480841,0.08510370739571123,0.08218751692411075,0.07902499000732208,0.0756222567821736,0.07200123970019219,0.06820107374866002,0.0642792935475432,0.06031258981971344,0.05639666264201267,0.052644252735941394,0.04917984945437528,0.04612915594201979,0.04360194559773293,0.04166961551464691,0.040343591617399095,0.03956458519503276,0.039210333580061554,0.03912043096847421,0.03912863012017659,0.03909241485851762,0.038914976871294714,0.03855991955842924,0.03806079683273675,0.03752613404609909,0.03713695490313335,0.03712966570683909,0.03775677465095472],[0.14552507639864284,0.14284582263120923,0.1401049429208714,0.13731898698272102,0.13450632397811685,0.13168669626382148,0.12888058127809668,0.1261083500072591,0.12338922858023078,0.12074009499430077,0.11817417434806878,0.11569972942113138,0.11331887266219173,0.11102664267128275,0.10881048557128546,0.10665025501968127,0.10451879556096504,0.10238311069025181,0.10020605231788456,0.09794841608283818,0.0955712973624425,0.0930385595266498,0.09031928578413226,0.08739012082366304,0.08423744846701788,0.0808593873224856,0.0772676097780636,0.07348899233902677,0.06956707575901434,0.06556323219149426,0.061557272112140855,0.057646935157306595,0.053945274791474894,0.050574455522527643,0.04765431020109493,0.04528496026682894,0.04352572917621929,0.04237689682315647,0.04177316682289351,0.04159413302058979,0.0416887748729378,0.041904920876278735,0.042115188492042176,0.04223563173989494,0.04223733222581385,0.04215232228373749,0.042074071048090016,0.042150619596343135,0.04256694278395781,0.04351459291585751],[0.14780805866410282,0.1453149100401806,0.1427635269476177,0.1401678435395373,0.13754305739238337,0.1349051860258135,0.13227047169553002,0.12965463400587107,0.12707198549750287,0.1245344453561956,0.12205050909744751,0.11962425437611278,0.11725448053397365,0.11493408720293503,0.11264979112420993,0.11038225861533861,0.10810669568233441,0.10579389421360523,0.10341168909525551,0.10092674581564148,0.09830657739946165,0.0955216857776684,0.09254773435349188,0.08936768083393958,0.08597382596490617,0.08236975773105518,0.07857218458818462,0.07461264646060316,0.07053905508294678,0.06641692360847697,0.06232996519199281,0.05837943162276849,0.05468111712333435,0.05135849571951639,0.04853043750019472,0.046293204940363014,0.04469965229370593,0.043742700988756274,0.04335155806780002,0.04340453342952581,0.04375413591785806,0.044255216365397455,0.044788450354884775,0.04527615824199722,0.04569094707302646,0.04605851853077612,0.046455113076367634,0.046998813154686625,0.047833519526410864,0.04910587152296003],[0.14999526389408593,0.14767214692198488,0.14529249722258852,0.14286772554603974,0.1404100464659017,0.13793205472798453,0.13544618441460293,0.13296405730957567,0.13049573971297446,0.12804894223159297,0.1256282132262986,0.12323419124080841,0.12086299187929879,0.11850580723836182,0.1161487889480815,0.1137732686307875,0.11135634385519227,0.10887182729539552,0.10629152698493732,0.1035868015084632,0.10073031960251722,0.09769795060494235,0.094470719694799,0.09103677703696982,0.08739334853879947,0.08354865274439084,0.07952377697595057,0.07535449690955896,0.07109298209281371,0.06680922956806389,0.06259186842689045,0.05854763185897004,0.05479828823636457,0.051473309574398184,0.04869656619122861,0.046566863598525854,0.045135897381363387,0.04439173121258056,0.044256781678194496,0.04460333543098468,0.04528062174055752,0.04614315399478019,0.04707276554063843,0.04799205639150159,0.048870355709926594,0.04972395830370317,0.05061160480007462,0.05162530152283812,0.05287645002928105,0.054478229493657715],[0.15207862957226423,0.14991003289968793,0.14768523671429443,0.14541326000486007,0.14310354967805824,0.14076558665259095,0.13840840350678266,0.13604002391447634,0.1336668443966702,0.13129299037643047,0.12891968987336958,0.12654471766223793,0.12416196836608581,0.12176121695443831,0.11932811835737925,0.11684448442802096,0.11428885771817676,0.11163738015871033,0.10886493417180712,0.10594651735926142,0.10285880225866872,0.09958183092864888,0.09610079998320582,0.09240790345339274,0.08850421572914757,0.08440161097122759,0.08012472317491773,0.07571294318031176,0.07122240830578727,0.06672783568340188,0.06232382928380821,0.05812488245875899,0.05426266174695647,0.05087844429632217,0.048108448566806336,0.04606159008332778,0.04479397468884542,0.04429025369682389,0.04446271703129483,0.04517074755301165,0.04625202177227333,0.0475528238324867,0.0489495200758557,0.05035989016006041,0.05174653038927669,0.05311484989115006,0.054507184701146794,0.05599367899610026,0.057660388096945125,0.05959557000733969],[0.15405295102643585,0.1520241528615999,0.14993841006787273,0.14780250613856655,0.14562334760065665,0.1434076046689902,0.14116128675310985,0.1388892648878919,0.1365947612289049,0.13427883423792702,0.1319398960768374,0.12957330478320284,0.12717107672456698,0.12472176355816414,0.12221053193680854,0.11961947376865373,0.11692816110942165,0.11411444464609477,0.11115548054077022,0.10802895941118162,0.10471450519519696,0.10119521153227568,0.0974592891341099,0.09350180860486465,0.0893265377458118,0.08494788803680009,0.0803929973732132,0.07570397661729551,0.07094031793072088,0.06618136568969157,0.06152851465913434,0.057106310309428344,0.05306076469232323,0.04955205395369961,0.046738138271172194,0.04474779505046746,0.04364819581280511,0.043420996822605605,0.043962174949676074,0.045108147673582025,0.046674649674539104,0.04849122809183718,0.05042273402656693,0.05237830794675818,0.05431194378013734,0.056218223263316255,0.05812523925309992,0.060085608150329,0.06216610846421316,0.06443668403252278],[0.15591550788709055,0.15401273574064792,0.15205145361932382,0.1500363795443327,0.14797210902447566,0.1458627916138671,0.14371176081848003,0.14152112995505217,0.1392913728014189,0.13702091409704703,0.13470576039176083,0.13233920552862297,0.12991164635105568,0.12741054243553146,0.12482054857046915,0.12212384067318993,0.11930064577518311,0.11632997599584627,0.1131905567013564,0.10986193191622734,0.10632572684431034,0.10256704894225488,0.09857601577563119,0.09434940988057873,0.08989247772862874,0.08522091083083022,0.08036306982203952,0.07536253085114608,0.07028103115382175,0.06520182603350273,0.06023324935303531,0.05551170999821704,0.05120217912776681,0.04749227844910965,0.04457421595518781,0.0426103578971157,0.04168806615239323,0.041785107514631006,0.04277032328145028,0.044442118297727505,0.0465810488243891,0.04899108107854679,0.051520772784786305,0.054068704910955424,0.05658029919751385,0.059040896275302755,0.06146738382529656,0.06389920248342307,0.0663890772861703,0.06899388526791267],[0.15766570254324838,0.15587623797550587,0.1540261048163099,0.15211813175126723,0.15015482851063647,0.14813809744853745,0.1460689128893389,0.14394698057044258,0.1417703942764417,0.1395353112815991,0.1372356719284258,0.1348629909699133,0.13240624866376768,0.12985190769474153,0.12718407778761304,0.12438484370650525,0.12143476494268325,0.11831354780345647,0.11500088402772372,0.11147744567531952,0.1077260249500955,0.10373281072422508,0.09948880160961521,0.09499136927459385,0.09024600636448873,0.08526832221872452,0.0800863878715625,0.07474357879584662,0.0693021102933726,0.06384747122613028,0.05849383273468064,0.05338997598802055,0.04872379656828416,0.04472024519245324,0.041622941902515184,0.039648772624865776,0.038919481474898224,0.039405825984477116,0.04093032611819606,0.043230360900814606,0.04603476053380215,0.049113866589740526,0.05229777674273078,0.05547536524174171,0.058585741694783436,0.06160806976907373,0.06455174899803831,0.06744730037892276,0.0703378910752842,0.07327153565914309],[0.15930471770422203,0.1576169567394897,0.15586597314874598,0.1540528833695064,0.15217832890805008,0.15024222075209348,0.14824346260618437,0.1461796645378032,0.14404686223252736,0.14183926031818453,0.1395490207164828,0.1371661183073922,0.13467828601741538,0.13207106959779158,0.12932800889905893,0.12643095769407778,0.12336054862934913,0.12009680447706823,0.11661989242512248,0.11291101562678907,0.10895343657433858,0.10473363101379135,0.10024258018332738,0.09547722466327459,0.09044212747211372,0.085151431117557,0.07963124912499775,0.0739227152317688,0.06808602997815713,0.062205986159171056,0.05639954654995295,0.05082579839314604,0.045697149083158486,0.041285986890290345,0.03791103061920262,0.03587787587847468,0.03536735572798179,0.0363354063979492,0.03852276189086652,0.04157027491748081,0.04513615299070166,0.04895276420700705,0.052834372764810573,0.05666474518713572,0.06038131364591866,0.06396136609244575,0.06741089780467453,0.07075547875510275,0.07403249053859041,0.07728439743349459],[0.16083519743423424,0.1592386754228063,0.15757615255391125,0.15584720772365743,0.1540508223138816,0.152185154601545,0.1502473013395494,0.1482330571162287,0.1461366848148341,0.14395071282617755,0.14166577631802088,0.13927052055763078,0.1367515838177568,0.13409367569614958,0.13127976383642284,0.12829137833110119,0.1251090389708862,0.1217128065761944,0.11808295660398287,0.114200771820545,0.1100494518851912,0.10561514215228938,0.10088809315691709,0.09586397811901679,0.09054542183965747,0.08494383670505948,0.07908173106485064,0.07299577100178091,0.06674106971049326,0.06039749318316943,0.054079235707031346,0.04794939633002751,0.04224086929658223,0.03728004274879158,0.03349183529313581,0.03132965528677124,0.031081380848894873,0.03266873552463957,0.035681505959688053,0.039610863737687574,0.04402866792351238,0.04863448587990863,0.05323688714173224,0.057723390103156226,0.06203635426615505,0.0661561251721867,0.07008924413912712,0.07385971853049025,0.07750210673379261,0.08105578993529777],[0.16226095409124391,0.16074634216397501,0.15916287405717627,0.1575087614070595,0.15578152348913316,0.15397778859215588,0.15209308878223976,0.1501216575937715,0.1480562422097542,0.14588794334406935,0.14360609709727518,0.14119821334032193,0.1386499845662012,0.1359453776153093,0.13306681832536246,0.12999547621093469,0.1267116530932889,0.1231952766302559,0.11942649746414878,0.11538638779862043,0.1110577403016942,0.10642597015864522,0.10148013111034017,0.09621407049848381,0.09062777249216494,0.0847289799701645,0.07853525789984989,0.07207679194871847,0.06540046030354728,0.05857618315655646,0.051707448419651504,0.04494954447848037,0.03854140219042629,0.03285685371737397,0.028459941868621125,0.026057756185776486,0.02614992423413445,0.028571681102215075,0.032619994115435,0.037567331370689766,0.042903343166212894,0.04831819141443419,0.05363392600491606,0.058753888478432784,0.06363255621135601,0.06825782291785223,0.07263990587281781,0.07680369399937781,0.08078294067211438,0.08461556275966686],[0.16358670227371733,0.16214578117933542,0.16063319681676133,0.1590459582291357,0.15738031055289642,0.15563156042638351,0.15379389937056331,0.15186023361487216,0.1498220303442738,0.1476691914973423,0.1453899668959288,0.14297091851037297,0.1403969469893784,0.13765139021414877,0.1347162016637158,0.13157221398489904,0.1281994906106292,0.12457776589463429,0.12068697240698112,0.11650785318373641,0.1120226573300645,0.10721592006962109,0.10207533407477334,0.09659272937764964,0.09076519752763426,0.08459642824915682,0.0780983867229727,0.07129357476505338,0.06421835221228082,0.05692829214206524,0.04950766222732997,0.042087755320530267,0.03488504322129609,0.02828319540519404,0.022989948787508686,0.020150837396807463,0.02073907398170992,0.024342522867218823,0.029670366224713397,0.03573323504646434,0.041996797442918954,0.048188724762871685,0.05416905921321011,0.059868376725825935,0.06525853495593444,0.07033759772766102,0.07512102066745698,0.07963572788855457,0.08391562420063163,0.08799792918096787],[0.16481781999360465,0.16344343602870276,0.16199473552579746,0.16046768332089806,0.15885742866388522,0.15715815201449332,0.1553629131680614,0.15346350818835433,0.15145034373588803,0.14931233817829653,0.14703685924473875,0.14460970785603935,0.14201515708578064,0.1392360540001027,0.1362539904632703,0.13304954702149008,0.129602611881186,0.12589277501046775,0.12189979576732045,0.11760414146286538,0.11298759419396938,0.10803392448451028,0.10272963329176905,0.09706476970521756,0.09103384203472613,0.08463685878728956,0.07788057158699688,0.07078006334383827,0.06336097761043454,0.05566303735202087,0.04774638646971967,0.039704741118162246,0.03169694658283479,0.024034858524804394,0.017456227806711272,0.013785998794746275,0.015225774746477903,0.02053886996829033,0.027322606952009085,0.03447495240541924,0.04157496116076118,0.0484413223815664,0.05498884650816574,0.06117956040268477,0.06700307321827649,0.0724670657866828,0.07759167678354384,0.0824055334946239,0.08694255981298728,0.09123923623975835],[0.1659601367177834,0.16464614362540372,0.1632554221225002,0.1617830445571593,0.1602232332308137,0.15856922630976064,0.15681314753741996,0.15494588633352216,0.15295699568957974,0.1508346158204183,0.1485654317314861,0.1461346726562261,0.14352616068563456,0.14072241487314568,0.13770481571624463,0.13445383329709087,0.13094932064585232,0.12717087222976087,0.123098246030081,0.11871184660228921,0.11399326596277318,0.10892587924534933,0.10349549299057006,0.09769104595056999,0.09150536598491374,0.0849359932556888,0.07798609241553876,0.07066550179888291,0.06299202350589811,0.05499319352834235,0.04670913497211131,0.03819821286473673,0.029551267502297345,0.020938936285905638,0.012837853502634606,0.0075784264329622295,0.01072329602582825,0.018146712998175135,0.026199530188155545,0.03418223067601053,0.04189589816623757,0.049257198952541756,0.056226941688574845,0.06279004361741622,0.06894764161904073,0.0747128434365119,0.08010774523220254,0.08516094355175689,0.08990528319200523,0.09437577622913433],[0.16701974755135165,0.1657609376370599,0.16442329985577417,0.16300115884681027,0.16148796989872435,0.15987620210833317,0.15815722719441694,0.1563212197852429,0.1543570756172174,0.1522523544688693,0.14999325475585423,0.14756462649402055,0.14495002879057142,0.14213183717084577,0.13909140494514902,0.13580928155016034,0.13226548946807676,0.12843986005051655,0.12431242746998675,0.1198638791961448,0.11507606093868732,0.10993253399329424,0.10441918345880802,0.09852487700472495,0.09224217606110775,0.08556810518190408,0.07850499257450168,0.07106140951646246,0.0632532692874561,0.055105227347779236,0.046652747686739264,0.03794590477652212,0.029058667266282544,0.020120738027777734,0.01149156758735133,0.0056255439453016184,0.010134931751340828,0.018364136477520835,0.02685503922951919,0.035162870915405486,0.04315631241445666,0.050774680907583726,0.05798725562052474,0.06478172101420093,0.07115922850820769,0.07713140131873865,0.08271800529346264,0.0879448825203417,0.09284202386233688,0.0974417625975987],[0.16800285259816286,0.16679487984988187,0.16550634787354926,0.16413097117225686,0.16266158909584993,0.16109006476543355,0.15940719109799226,0.15760260911413046,0.15566474419136592,0.1535807662148549,0.15133657964095085,0.14891684930735105,0.14630506739918098,0.14348366634038148,0.14043418157677218,0.13713746732725257,0.13357396749848766,0.12972404319697478,0.12556835775411956,0.12108832004432293,0.11626658729434022,0.11108762979743153,0.10553836236115507,0.09960885168345854,0.09329311667075858,0.08659005315144827,0.07950454250125996,0.07204886172960362,0.0642446413471417,0.05612592712189909,0.047744722174195946,0.03918282980856702,0.030582251716855087,0.022241156096252074,0.014987896916772651,0.011446566276263654,0.014599777402921347,0.02152543637692067,0.02945951293538766,0.037532368524341386,0.04544483261924706,0.053066027627568936,0.060330861161672085,0.06720755327617493,0.07368471507101988,0.07976495393058569,0.08546098853466409,0.09079285339422996,0.09578564520693245,0.1004675954542942],[0.16891562037244617,0.1677549180303877,0.16651233459783044,0.1651811044919892,0.16375359327966793,0.16222121122214034,0.1605743351111161,0.15880224307086174,0.15689306739453873,0.15483377072622506,0.15261015097253233,0.15020688022280176,0.1476075826869524,0.14479495625917346,0.14175094184095305,0.13845694408947096,0.13489410690328268,0.1310436468515975,0.12688724807143092,0.1224075231389974,0.11758854642736002,0.11241647007789307,0.106880238967876,0.10097243186241865,0.09469027501168191,0.08803690932291633,0.0810230588331862,0.07366938191024296,0.06601007034785335,0.058098901724752586,0.050020494206362176,0.041913493036716626,0.034023171365786455,0.026828318392223518,0.021317484509596533,0.01916853983061234,0.021405796328812256,0.02682381397601863,0.03373706853604237,0.041190440040570195,0.0487299327717161,0.056129959517494984,0.06327081621861551,0.07008769725986595,0.07654782684266948,0.08263897098720015,0.08836289818545223,0.09373116877197424,0.0987621187744335,0.1034785245311215],[0.16976407401357507,0.16864776878133947,0.16744869819890656,0.16615973874393583,0.16477291519558157,0.1632793279233617,0.16166908950994544,0.15993127499296023,0.15805389035768175,0.1560238641483369,0.15382706718141628,0.15144836534452766,0.1488717103711153,0.14608027333769952,0.1430566255028736,0.1397829710906855,0.13624143684448986,0.13241442381791482,0.12828502817771262,0.12383754014183658,0.11905803415329419,0.11393506997490224,0.10846053528577866,0.10263067864643646,0.09644741312732144,0.08992002654935945,0.08306753619026015,0.0759221190531371,0.06853442800754457,0.060982370127773126,0.05338649020052857,0.045938190782256146,0.03895193433694344,0.03295249431313207,0.0287582613460494,0.027320664964852744,0.02904417418516555,0.03334225456817187,0.03922232295521269,0.045899490929558265,0.052887584592189625,0.059902155947122844,0.0667760918545368,0.0734106827137302,0.07974909435291522,0.0857615947649328,0.09143679756975147,0.09677606243016841,0.10178963123907811,0.1064937817446752],[0.17055399895153153,0.16947982383608867,0.16832245247298397,0.16707451720564523,0.1657278254763766,0.1642733001746146,0.16270093027928353,0.16099973579247687,0.15915775129145723,0.1571620326808689,0.15499869190775623,0.1526529645226415,0.1501093150617788,0.1473515853409179,0.1443631909673198,0.14112737180487153,0.13762750292174952,0.133847473930669,0.12977214691891792,0.12538790684565257,0.12068332412547185,0.11564995837648094,0.11028334710472634,0.10458424707869501,0.09856023574626697,0.09222784673156545,0.08561552779426057,0.07876790812498392,0.0717522059900221,0.06466818520348812,0.057663929788319385,0.050960489713132454,0.04488686229685563,0.03991428443672651,0.03663830788538497,0.03560716239236345,0.03700401660285618,0.04050147665720907,0.045490953385392434,0.05138585928200734,0.05774683750265986,0.06427683390835488,0.0707822167749413,0.07713876587827159,0.08326850816032541,0.08912486151226609,0.09468304862475031,0.09993369381564393,0.10487834672213915,0.10952620742470125],[0.1712908705718471,0.17025707816213764,0.16914011636651516,0.16793247839626685,0.1666258677958682,0.16521115128061384,0.16367832277775407,0.16201648246281725,0.16021383491475125,0.1582577108028089,0.15613461677327403,0.15383031844687614,0.15132996170654875,0.14861823780967373,0.14567959838571432,0.14249852720152226,0.13905987686482582,0.13534928063698803,0.1313536525972882,0.1270617940795993,0.12246513141411988,0.11755862084891631,0.11234187316646956,0.10682057626778477,0.10100833416994368,0.09492910370882625,0.08862050780453293,0.08213845109095057,0.0755636672778376,0.0690110467467071,0.06264260357505938,0.056683964994790226,0.05144022904514184,0.047296377283363306,0.04467104303896436,0.0438958654034463,0.04506311378764335,0.04797109144229883,0.05222679232720942,0.057401678077684405,0.06312881395780616,0.06912951963240979,0.07520443553550088,0.08121557576443904,0.08706998332417426,0.09270729559069986,0.09809078474387994,0.10320093622879621,0.10803076950268205,0.11258234324067891],[0.17197980033243296,0.17098507815381805,0.1699076652889967,0.16874001156872562,0.16747381958411123,0.16610000948751358,0.16460869586133237,0.1629891803012872,0.16122996370506018,0.15931878258592194,0.15724267405837342,0.1549880744956155,0.15254095727957992,0.14988701561651643,0.14701189716433444,0.14390149833685453,0.14054232778838577,0.13692195098310886,0.1330295312642121,0.12885648795837376,0.12439729951356915,0.11965049054410413,0.11461985750044758,0.10931601067390458,0.10375834321558836,0.09797758376722276,0.09201914912339405,0.08594757920878272,0.0798523731567283,0.07385544322241071,0.06811988157609998,0.06285819365784084,0.058334692492924244,0.05485128385953584,0.05270288380404702,0.05210068884550651,0.05309508051892156,0.05555270292359359,0.0592074878908181,0.06374508081371828,0.0688694713908056,0.07433452018827053,0.07994973047222417,0.08557407222816911,0.09110655245158616,0.09647727535021201,0.101640076204727,0.10656675012758744,0.1112425894694708,0.11566292080333732],[0.1726254986930077,0.17166888809440115,0.17063050223151788,0.16950283366680224,0.16827767605595814,0.16694610037077107,0.16549844399627292,0.16392431624215434,0.1622126241671599,0.1603516229796027,0.15832899566443878,0.1561319669263155,0.15374745707193385,0.15116228214546648,0.14836340756249236,0.14533826377609374,0.1420751343089098,0.1385636290071265,0.1347952589007806,0.13076413397237865,0.12646781195066972,0.12190833560519969,0.11709350866780405,0.11203847711053831,0.10676770306642548,0.10131744103442136,0.09573884227828874,0.0901018019619286,0.08449957327020909,0.07905389474970034,0.0739197134899075,0.06928727319519086,0.06537730719115399,0.06242329073399579,0.06063630092404809,0.060157173134795516,0.06101517536460287,0.06311746018524773,0.06627662035342388,0.07025892348165189,0.07482862899215584,0.07977547607704129,0.08492582124609879,0.09014341691946874,0.09532536163799196,0.10039657959435105,0.10530441326276552,0.11001390254454618,0.11450385633137858,0.11876364534337891],[0.17323225313647497,0.17231307297150633,0.1713134465805568,0.1702259854405383,0.1690426550410213,0.1677547619278904,0.16635295434558137,0.16482723992875772,0.16316702426365515,0.16136117452856555,0.15939811285009334,0.15726594450462697,0.15495262669264237,0.1524461843712909,0.1497349806202825,0.1468080503310254,0.14365550776911443,0.14026904091596673,0.13664250863013075,0.1327726607939837,0.12866000694154536,0.12430986554260791,0.11973363404374159,0.11495032818354042,0.10998844574373383,0.10488820925696232,0.09970422219177778,0.09450850939520414,0.08939376011790905,0.08447627840560265,0.07989758311992001,0.07582276116648397,0.07243280972048405,0.06990816783862773,0.06840294186111129,0.06801480526512026,0.06876161190965153,0.07057616387190817,0.07332211276488948,0.07682286591721248,0.08089107329168083,0.08535028972683475,0.09004686524708015,0.09485412697789218,0.09967188227805167,0.10442366019448716,0.10905317836015391,0.11352080149901522,0.11780032144603529,0.1218761619897055],[0.1738039194977483,0.17292169564891388,0.17196073840473353,0.1709138442520206,0.1697732198687142,0.16853047929917425,0.1671766553408768,0.16570222850414504,0.16409717727785478,0.16235105383264437,0.16045308973547637,0.15839233675928183,0.15615784848136346,0.15373890911644308,0.1511253169774627,0.14830773116277854,0.1452780916044279,0.1420301245542742,0.13855994799842397,0.13486679440023383,0.1309538714996277,0.12682938533167937,0.1225077523839153,0.1180110281652744,0.11337057392192926,0.10862896516186414,0.10384210312960274,0.09908140366973192,0.09443577823530441,0.09001285691240501,0.08593852274789242,0.08235340522978407,0.07940478392016627,0.07723290207551209,0.07595254096009832,0.07563370316744847,0.07628771973501962,0.07786448862836692,0.0802621570945009,0.08334518612490402,0.08696421505921069,0.09097245938212023,0.09523645518792916,0.09964147940019408,0.10409309800216547,0.10851637071112563,0.11285387099556009,0.11706325694906397,0.12111480331879723,0.12498909677039784]],"type":"contour"},{"hoverinfo":"text","legendgroup":"In-sample","marker":{"color":"black","opacity":0.5,"symbol":1},"mode":"markers","name":"In-sample","text":["Arm 0_0\u003cbr\u003eaccuracy: 0.48 (SEM: None)\u003cbr\u003eC: 3.42871e-05\u003cbr\u003egamma: 0.000601517","Arm 1_0\u003cbr\u003eaccuracy: 0.496 (SEM: None)\u003cbr\u003eC: 55.3814\u003cbr\u003egamma: 5357.65","Arm 2_0\u003cbr\u003eaccuracy: 0.808 (SEM: None)\u003cbr\u003eC: 690.339\u003cbr\u003egamma: 0.00857996","Arm 3_0\u003cbr\u003eaccuracy: 0.78 (SEM: None)\u003cbr\u003eC: 562386\u003cbr\u003egamma: 0.000184708","Arm 4_0\u003cbr\u003eaccuracy: 0.776 (SEM: None)\u003cbr\u003eC: 923227\u003cbr\u003egamma: 0.0545368","Arm 5_0\u003cbr\u003eaccuracy: 0.812 (SEM: None)\u003cbr\u003eC: 8059.7\u003cbr\u003egamma: 0.00137448","Arm 6_0\u003cbr\u003eaccuracy: 0.8 (SEM: None)\u003cbr\u003eC: 657.413\u003cbr\u003egamma: 1e-06","Arm 7_0\u003cbr\u003eaccuracy: 0.792 (SEM: None)\u003cbr\u003eC: 410.754\u003cbr\u003egamma: 0.000125186","Arm 8_0\u003cbr\u003eaccuracy: 0.824 (SEM: None)\u003cbr\u003eC: 57567.2\u003cbr\u003egamma: 1e-06"],"visible":true,"x":[3.428714353076635e-05,55.38136172368294,690.33938400923,562386.4909845794,923227.2828835016,8059.70102430378,657.4126489790578,410.75370137586805,57567.15135812723],"xaxis":"x","y":[0.0006015170467586964,5357.645905431237,0.008579956814279222,0.00018470757289220898,0.05453675687985037,0.0013744807130274097,1e-06,0.00012518635614469357,1e-06],"yaxis":"y","type":"scatter"},{"hoverinfo":"text","legendgroup":"In-sample","marker":{"color":"black","opacity":0.5,"symbol":1},"mode":"markers","name":"In-sample","showlegend":false,"text":["Arm 0_0\u003cbr\u003eaccuracy: 0.48 (SEM: None)\u003cbr\u003eC: 3.42871e-05\u003cbr\u003egamma: 0.000601517","Arm 1_0\u003cbr\u003eaccuracy: 0.496 (SEM: None)\u003cbr\u003eC: 55.3814\u003cbr\u003egamma: 5357.65","Arm 2_0\u003cbr\u003eaccuracy: 0.808 (SEM: None)\u003cbr\u003eC: 690.339\u003cbr\u003egamma: 0.00857996","Arm 3_0\u003cbr\u003eaccuracy: 0.78 (SEM: None)\u003cbr\u003eC: 562386\u003cbr\u003egamma: 0.000184708","Arm 4_0\u003cbr\u003eaccuracy: 0.776 (SEM: None)\u003cbr\u003eC: 923227\u003cbr\u003egamma: 0.0545368","Arm 5_0\u003cbr\u003eaccuracy: 0.812 (SEM: None)\u003cbr\u003eC: 8059.7\u003cbr\u003egamma: 0.00137448","Arm 6_0\u003cbr\u003eaccuracy: 0.8 (SEM: None)\u003cbr\u003eC: 657.413\u003cbr\u003egamma: 1e-06","Arm 7_0\u003cbr\u003eaccuracy: 0.792 (SEM: None)\u003cbr\u003eC: 410.754\u003cbr\u003egamma: 0.000125186","Arm 8_0\u003cbr\u003eaccuracy: 0.824 (SEM: None)\u003cbr\u003eC: 57567.2\u003cbr\u003egamma: 1e-06"],"visible":true,"x":[3.428714353076635e-05,55.38136172368294,690.33938400923,562386.4909845794,923227.2828835016,8059.70102430378,657.4126489790578,410.75370137586805,57567.15135812723],"xaxis":"x2","y":[0.0006015170467586964,5357.645905431237,0.008579956814279222,0.00018470757289220898,0.05453675687985037,0.0013744807130274097,1e-06,0.00012518635614469357,1e-06],"yaxis":"y2","type":"scatter"}],                        {"annotations":[{"font":{"size":14},"showarrow":false,"text":"Mean","x":0.25,"xanchor":"center","xref":"paper","y":1,"yanchor":"bottom","yref":"paper"},{"font":{"size":14},"showarrow":false,"text":"Standard Error","x":0.8,"xanchor":"center","xref":"paper","y":1,"yanchor":"bottom","yref":"paper"},{"showarrow":false,"text":"x-param:","x":0.26,"xanchor":"left","xref":"paper","y":-0.26,"yanchor":"top","yref":"paper"},{"showarrow":false,"text":"y-param:","x":0.26,"xanchor":"left","xref":"paper","y":-0.4,"yanchor":"top","yref":"paper"}],"autosize":true,"height":450,"hovermode":"closest","legend":{"orientation":"v","x":0,"y":-0.2,"yanchor":"top"},"margin":{"b":100,"l":35,"pad":0,"r":35,"t":35},"title":{"text":"accuracy"},"updatemenus":[{"buttons":[{"args":[{"x":[[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],[3.428714353076635e-05,55.38136172368294,690.33938400923,562386.4909845794,923227.2828835016,8059.70102430378,657.4126489790578,410.75370137586805,57567.15135812723],[3.428714353076635e-05,55.38136172368294,690.33938400923,562386.4909845794,923227.2828835016,8059.70102430378,657.4126489790578,410.75370137586805,57567.15135812723],[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],[3.428714353076635e-05,55.38136172368294,690.33938400923,562386.4909845794,923227.2828835016,8059.70102430378,657.4126489790578,410.75370137586805,57567.15135812723],[3.428714353076635e-05,55.38136172368294,690.33938400923,562386.4909845794,923227.2828835016,8059.70102430378,657.4126489790578,410.75370137586805,57567.15135812723]],"y":[[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],[3.428714353076635e-05,55.38136172368294,690.33938400923,562386.4909845794,923227.2828835016,8059.70102430378,657.4126489790578,410.75370137586805,57567.15135812723],[3.428714353076635e-05,55.38136172368294,690.33938400923,562386.4909845794,923227.2828835016,8059.70102430378,657.4126489790578,410.75370137586805,57567.15135812723],[1e-06,1.757510624854793e-06,3.0888435964774785e-06,5.428675439323859e-06,9.540954763499944e-06,1.67683293681101e-05,2.94705170255181e-05,5.1794746792312125e-05,9.102981779915228e-05,0.00015998587196060574,0.0002811768697974231,0.0004941713361323833,0.000868511373751352,0.0015264179671752333,0.0026826957952797246,0.004714866363457394,0.008286427728546842,0.014563484775012445,0.025595479226995333,0.04498432668969444,0.07906043210907701,0.1389495494373136,0.244205309454865,0.42919342601287785,0.7543120063354607,1.325711365590108,2.329951810515372,4.094915062380427,7.196856730011514,12.648552168552959,22.229964825261955,39.06939937054613,68.66488450042998,120.67926406393264,212.09508879201925,372.7593720314938,655.1285568595496,1151.3953993264481,2023.5896477251556,3556.4803062231213,6250.551925273976,10985.411419875572,19306.977288832455,33932.217718953296,59636.23316594637,104811.3134154683,184206.99693267164,323745.754281764,568986.6029018281,1000000.0],[1e-06,1.757510624854793e-06,3.0888435964774785e-06,5.428675439323859e-06,9.540954763499944e-06,1.67683293681101e-05,2.94705170255181e-05,5.1794746792312125e-05,9.102981779915228e-05,0.00015998587196060574,0.0002811768697974231,0.0004941713361323833,0.000868511373751352,0.0015264179671752333,0.0026826957952797246,0.004714866363457394,0.008286427728546842,0.014563484775012445,0.025595479226995333,0.04498432668969444,0.07906043210907701,0.1389495494373136,0.244205309454865,0.42919342601287785,0.7543120063354607,1.325711365590108,2.329951810515372,4.094915062380427,7.196856730011514,12.648552168552959,22.229964825261955,39.06939937054613,68.66488450042998,120.67926406393264,212.09508879201925,372.7593720314938,655.1285568595496,1151.3953993264481,2023.5896477251556,3556.4803062231213,6250.551925273976,10985.411419875572,19306.977288832455,33932.217718953296,59636.23316594637,104811.3134154683,184206.99693267164,323745.754281764,568986.6029018281,1000000.0],[0.0006015170467586964,5357.645905431237,0.008579956814279222,0.00018470757289220898,0.05453675687985037,0.0013744807130274097,1e-06,0.00012518635614469357,1e-06],[0.0006015170467586964,5357.645905431237,0.008579956814279222,0.00018470757289220898,0.05453675687985037,0.0013744807130274097,1e-06,0.00012518635614469357,1e-06]],"z":[[[0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072,0.4791214492797072],[0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489,0.4765055534585489],[0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062,0.474022169877062],[0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303,0.47169059147778303],[0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806,0.46953024493506806],[0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483,0.4675604804196483],[0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406,0.46580034552776406],[0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141,0.464268347911141],[0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177,0.46298221227977177],[0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435,0.4619586385001435],[0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241,0.4612130683894241],[0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618,0.460759469418618],[0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997,0.46061014379633997],[0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537,0.4607755712354537],[0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573,0.46126429305734573],[0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341,0.4620828441449341],[0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242,0.463235737632242],[0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404,0.46472550516376404],[0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176,0.46655279314062176],[0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534,0.46871651266704534],[0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034,0.4712140379785034],[0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264,0.47404144499184264],[0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956,0.4771937782300956],[0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823,0.4806653306296823],[0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617,0.4844499164474617],[0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583,0.48854111238948583],[0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319,0.4929324358715319],[0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286,0.4976174216749286],[0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292,0.5025895489367292],[0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241,0.5078419594148241],[0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515,0.5133668959419515],[0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371,0.5191547792223371],[0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735,0.5251928383080735],[0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473,0.5314632335936473],[0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315,0.5379407073402315],[0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737,0.5445900540230737],[0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509,0.5513641664407509],[0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895,0.5582037612936895],[0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897,0.5650394193314897],[0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661,0.5717954076467661],[0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306,0.5783941007195306],[0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263,0.5847600760754263],[0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815,0.5908234648302815],[0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757,0.596522458273757],[0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384,0.6018050124855384],[0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682,0.6066298444372682],[0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287,0.610966827689287],[0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235,0.614796895294235],[0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307,0.61811155046307],[0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948,0.6209120758628948]],[[0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897,0.16202601432683897],[0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808,0.16049810146744808],[0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832,0.15890181711905832],[0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514,0.15723559333986514],[0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293,0.15549718418400293],[0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873,0.15368346270841873],[0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547,0.15179021044169547],[0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497,0.1498119090349497],[0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774,0.14774154594500774],[0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342,0.14557044775120342],[0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128,0.14328815585210128],[0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446,0.14088235962863446],[0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893,0.13833890156363893],[0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456,0.13564186724515456],[0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099,0.1327737707514099],[0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063,0.12971584285721063],[0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922,0.12644842618300922],[0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748,0.12295147830430748],[0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481,0.11920518150298481],[0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475,0.11519065688763475],[0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659,0.11089078173349659],[0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487,0.1062911129670487],[0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673,0.10138092801621673],[0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931,0.09615440887540931],[0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883,0.09061201999671883],[0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147,0.08476217264025147],[0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923,0.07862334123700923],[0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243,0.0722269275832243],[0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963,0.06562140778332963],[0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885,0.058878743222541885],[0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405,0.0521048635936405],[0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294,0.045457452004306294],[0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277,0.03917603119827277],[0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464,0.033627898944790464],[0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382,0.02935166288989382],[0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644,0.027000878460360644],[0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498,0.027027256901948498],[0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927,0.02928732207605927],[0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737,0.03314297639609737],[0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282,0.03790870423320282],[0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906,0.043086039566320906],[0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147,0.04836405629526147],[0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558,0.05356082590770558],[0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169,0.05857610811982169],[0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212,0.06336186025995212],[0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031,0.0679044391709031],[0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164,0.07221327583257164],[0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128,0.07631298900853128],[0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071,0.08023737115637071],[0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513,0.08402451052209513]],[],[],[[0.4768731329347412,0.4755253693607116,0.47454994543099366,0.4739929085393086,0.4739016227380968,0.47432421635242356,0.4753089000604388,0.47690314697483505,0.479152731839036,0.4821006351176183,0.485785830062194,0.4902419868043849,0.4954961461608459,0.5015674345459795,0.50846590581502,0.516191600545808,0.5247339035333387,0.5340712548186973,0.5441712323150065,0.5549909835422759,0.5664779499685177,0.5785708069897874,0.5912005374572623,0.6042915638752391,0.6177628784974722,0.6315291261040331,0.6455016072877626,0.6595891784878974,0.6736990282032962,0.6877373073999765,0.7016095877031033,0.7152211162802317,0.7284768356622765,0.7412811463327041,0.7535374177478387,0.7651473074956263,0.7760100315157432,0.7860218301439025,0.7950759632289258,0.8030635934118483,0.8098759500279108,0.8154087822613035,0.8195692748982392,0.822284328513949,0.8235099685098549,0.8232420874042436,0.8215286025929815,0.8184742146323478,0.8142253922201969,0.8089510238160853],[0.473373063454019,0.4718763661183611,0.47075563969226997,0.47005876666282204,0.4698351773727626,0.470135296695335,0.471009850158852,0.4725090168490019,0.4746814213476184,0.4775729654625171,0.4812255136226994,0.4856754642320297,0.49095226253854796,0.4970769360901087,0.5040607560624316,0.5119041385406055,0.5205958910966301,0.5301128781796244,0.5404201288619978,0.5514713554435998,0.5632098067956466,0.5755693565436515,0.5884757246651835,0.601847745822633,0.6155986199524959,0.6296371026524241,0.6438686099830417,0.6581962223823566,0.672521575245121,0.6867456201607112,0.7007692323818728,0.7144936293256167,0.7278205559759806,0.7406521929035252,0.7528907618762407,0.7644378564986576,0.7751936229201638,0.7850560553864983,0.7939208159202293,0.8016820658990601,0.8082348796677311,0.813480096336799,0.8173315980582209,0.8197249537146074,0.820626929781777,0.8200458831601198,0.8180422165898518,0.8147305384788522,0.8102653067521226,0.8048213003572738],[0.4700235377784523,0.46838128460010287,0.4671180798260149,0.4662835670967987,0.4659291776805927,0.46610758247186324,0.4668719937726474,0.468275299663087,0.47036901756748306,0.4732020612616865,0.47681932870885796,0.4812601383712768,0.4865565696909347,0.49273179734615397,0.49979854223029163,0.5077577831777994,0.5165978683967776,0.5262941260396228,0.5368090050393289,0.5480927008659118,0.5600841614383836,0.5727123417273484,0.5858975812983661,0.5995530055076568,0.6135858842634551,0.6278989120179669,0.6423913939448014,0.6569603348224883,0.6715014295748141,0.6859099489059971,0.7000815013967495,0.7139126366744671,0.7273012361769615,0.7401466250979267,0.7523493433991445,0.7638105550603881,0.7744311785534259,0.784111004638151,0.792748304296835,0.8002406328766785,0.8064876357151798,0.8113964848856665,0.8148896929477251,0.8169142555834189,0.8174512662650016,0.8165253705018625,0.8142119236673402,0.8106357529329195,0.8059579178966036,0.8003571925465778],[0.46684794456721357,0.465065138620231,0.46366393631310393,0.46269564762644594,0.4622136130569515,0.4622726669559672,0.4629284428736184,0.4642364991971612,0.4662512455780474,0.46902465662450155,0.4726047713412023,0.4770339976191195,0.4823472732169698,0.4885701781478473,0.49571714200010203,0.5037899276927517,0.512776577210815,0.5226509567858253,0.5333729436981622,0.5448891877736426,0.5571343004130189,0.5700322963702527,0.5834981329668237,0.5974392356343242,0.6117569459904973,0.6263478666732132,0.6411051019920517,0.655919405764249,0.670680249458221,0.6852768166967075,0.6995989153897917,0.7135377771905574,0.7269866873574163,0.739841361080471,0.7519999659327075,0.7633627074876252,0.7738309872348721,0.7833063614139519,0.7916898942241006,0.7988828906329232,0.8047900942832796,0.8093258842269825,0.8124229043487302,0.8140417703908118,0.8141804901098544,0.8128822165690227,0.8102388719168767,0.8063869356662279,0.8014943064727208,0.7957427415008578],[0.463868859074413,0.4619521545932106,0.4604191348778763,0.4593226623059485,0.4587178694683405,0.45866163901390955,0.45921191999343003,0.46042685486664153,0.4623636916239913,0.46507745904132886,0.4686193925559692,0.4730351175820095,0.4783626312412478,0.48463017625626437,0.49185416895992856,0.5000374081943233,0.5091678157248481,0.5192179032596635,0.5301450252544819,0.5418923161627951,0.554390101263456,0.567557547498123,0.5813043654537953,0.5955324436424446,0.610137360040163,0.6250097610500681,0.640036624494985,0.6551024349168366,0.6700903001443572,0.6848830300319381,0.6993641822162502,0.713419055490474,0.7269355787686544,0.7398050041917116,0.751922273823351,0.7631859112436321,0.7734973415570673,0.7827597611939048,0.7908771720867125,0.797754875471794,0.8033029739052464,0.8074435011641173,0.81012012870719,0.8113084249522705,0.8110247274676968,0.8093318611837279,0.8063395872579641,0.8021977511396923,0.7970823263534553,0.7911780587661557],[0.4611075803276666,0.4590652618060343,0.45740829838945246,0.4561909748042117,0.45547007581768617,0.4553043863080964,0.4557540246971662,0.45687958055600997,0.45874102550130086,0.4613963671729889,0.4649000217166402,0.4693008954305624,0.47464019856323003,0.48094907311046753,0.48824620672606095,0.4965357100902878,0.5058055991045668,0.5160271672575083,0.527155335051547,0.5391298184610889,0.5518768082945362,0.5653108493212575,0.5793366973833001,0.5938510376699175,0.6087440272471274,0.6239006735079479,0.6392020849193084,0.6545266396968179,0.6697511172784423,0.6847518291325955,0.6994057697676019,0.7135917845803293,0.7271917163869979,0.7400914454821955,0.7521816803160384,0.7633582989658496,0.7735220261439544,0.7825773714365218,0.7904312948821587,0.7969931669122943,0.8021783844707336,0.8059166333053988,0.8081629251355072,0.8089083399870389,0.8081880851056317,0.8060851593785883,0.8027280755210526,0.7982816121796613,0.7929313937598251,0.7868658336850293],[0.4585836496096847,0.4564255552219679,0.45465415026256084,0.4533249996884061,0.4524963820347174,0.4522288115286888,0.45258439254107646,0.4536259748507467,0.455416074783535,0.45801552510714133,0.4614818176705357,0.4658671115475701,0.47121590469666746,0.47756242441922914,0.4849279005216799,0.49331804518632105,0.5027212045287568,0.5131076133107647,0.5244298876834139,0.5366245004706698,0.5496137804812196,0.5633080287738945,0.5776075089490613,0.5924042143641062,0.6075834046103519,0.623024948387983,0.6386045288149351,0.6541947725353524,0.669666361754523,0.6848891805341767,0.6997335329526144,0.7140714490450131,0.7277780614794218,0.7407329875435497,0.7528215835219733,0.7639358525641632,0.7739746999407958,0.7828432210167416,0.7904510863084444,0.7967115881460501,0.8015450396945202,0.8048884667649013,0.8067082222655502,0.807011014027068,0.8058509036824534,0.8033310042700371,0.7995989084219484,0.7948353588807233,0.7892370484158989,0.7829969976045822],[0.4563143675689017,0.4540517499017149,0.45217689990424037,0.4507465130434648,0.4498201901010837,0.4494599810821808,0.44972976195939146,0.45069441141986527,0.45241875016625394,0.454966200903697,0.4583971241102488,0.4627667860903242,0.46812292934269006,0.4745029592425939,0.48193087198547524,0.4904142680842908,0.49994207287542225,0.510483638963503,0.5219894542368279,0.5343930235338619,0.54761323295119,0.561556688840716,0.5761198000126517,0.5911905503997392,0.6066499925022353,0.622373524012451,0.6382320201031422,0.6540928949428495,0.669821162833659,0.6852805629571237,0.7003348010845806,0.7148489442814963,0.7286909765767524,0.7417334790215119,0.7538553292844075,0.7649432167240925,0.7748926364258573,0.7836078797961952,0.7910005453898564,0.7969874281597463,0.8014932023279684,0.8044619969052734,0.8058716268373467,0.805744437874879,0.8041529826879946,0.8012198501221107,0.7971111808331126,0.7920237101741968,0.7861659451540843,0.7797363400471893],[0.45431433119648906,0.45195965142963607,0.4499936378352924,0.44847396311942417,0.4474613711320791,0.4470192404495538,0.447212982047129,0.44810923770825034,0.44977484057224143,0.4522754935037263,0.4556741151728149,0.4600287991998048,0.4653903327586328,0.4717992416743398,0.47928241243301517,0.48784958927036537,0.49749052726741916,0.5081738869447125,0.5198482700264543,0.532444626900841,0.5458789985000629,0.5600550250729128,0.5748660609723337,0.5901969084737124,0.6059252384001959,0.6219227791528404,0.638056357325183,0.6541888711855794,0.6701802751944235,0.6858886493389271,0.7011714201273633,0.7158867880698055,0.7298953951732242,0.7430622287520938,0.7552586949006659,0.7663646934499879,0.7762703730932536,0.7848770357417135,0.7920964155235881,0.7978479266962543,0.8020602670977934,0.8046851312155512,0.805712349476806,0.805179944479855,0.8031783426718839,0.7998484187334189,0.7953733373962104,0.7899644122159285,0.783841345255066,0.777208296423801],[0.452595014825889,0.45016167106112853,0.4481177744033432,0.44652182065837964,0.4454355141402054,0.44492334743354384,0.4450520165515312,0.44588963802667964,0.44750472901342564,0.449964905271887,0.4533352449360901,0.4576762584530958,0.46304139811616934,0.4694740394453159,0.4770038975545401,0.4856430290807928,0.4953822545351635,0.5061897528468087,0.5180125987388904,0.530779800506744,0.5444053545423111,0.5587908297574768,0.5738274533789184,0.5893977739915696,0.6053769936504646,0.6216340601251467,0.6380326071656801,0.6544318278283632,0.6706873636426182,0.6866522901975072,0.7021782763879832,0.71711698793164,0.7313217920201461,0.7446497924044209,0.7569641714828653,0.7681367202214205,0.7780502739289045,0.7866005200453621,0.7936963095383701,0.7992577624010346,0.8032183047039616,0.8055386367732565,0.80622142382142,0.8053203472342096,0.802942876467031,0.7992465620580966,0.7944292572851154,0.7887139895736391,0.7823289367087695,0.7754827995755513],[0.45116442052442834,0.4486664166503261,0.446558560083926,0.44490001525447526,0.44375326269083515,0.44318369070779984,0.44325902337822226,0.44404855131877335,0.44562212631255305,0.44804887448402325,0.45139557552622267,0.45572464725159034,0.4610916654388712,0.4675423389052224,0.4751088528601588,0.48380554175485824,0.49362448041819773,0.5045336399392226,0.5164791545709053,0.5293889631056192,0.5431760065371976,0.55774079205652,0.5729734142862409,0.5887551383083389,0.6049596432474076,0.6214540194171069,0.6380996078687218,0.6547527685995074,0.6712656624084586,0.6874871309444187,0.703263759031861,0.718441201328934,0.7328658488051655,0.7463868936848426,0.7588588133802093,0.7701442143090879,0.7801168222191944,0.7886641405517599,0.7956890092101105,0.801110175934095,0.8048666543761387,0.8069297017066401,0.8073156216269812,0.8060936110945064,0.8033871481928878,0.7993685118673794,0.7942473538678941,0.7882546750463373,0.7816227377748989,0.774561276254639],[0.4500268221218676,0.44747838979338866,0.4453207257274702,0.4436135062494461,0.44241980090519223,0.44180567151662037,0.4418396078098128,0.44259176607745077,0.44413297181217626,0.44653344091443403,0.4498611668275291,0.45417991266010027,0.4595467378816871,0.4660089783619589,0.47360058619175377,0.4823377223147444,0.49221376234025743,0.5031969668973293,0.5152334907441088,0.5282513093326076,0.542163398987488,0.556870247503118,0.5722618122919043,0.58821903273289,0.6046149951905655,0.621315843152961,0.6381815208955206,0.6550664368271488,0.6718201319982682,0.6882880398425232,0.7043124245839557,0.7197335869484864,0.7343914250454268,0.7481274317715264,0.7607871900477773,0.7722233781819785,0.7822991943475006,0.7908919425513449,0.7978964801021795,0.8032290917088368,0.806834114722313,0.8086940387938868,0.808839313660642,0.8073542433718848,0.8043769469222579,0.8000920138942876,0.7947174333028779,0.7884879615145483,0.7816355078345503,0.7743679309425789],[0.4491826232914164,0.446597815369821,0.4444042765892694,0.442662032250267,0.4414345467379984,0.4407883252824246,0.44079235193540833,0.4415173300726497,0.4430346861715071,0.4454152912467023,0.4487278470346495,0.45303687567995116,0.4584002421554715,0.4648661277909763,0.47246936102812437,0.4812270032115027,0.4911334539223847,0.5021582233240588,0.5142487326340182,0.5273341655305684,0.5413286164337667,0.5561335629914399,0.5716397779173333,0.5877287858975786,0.6042739631309146,0.621141371049542,0.6381904117524657,0.6552743905160434,0.6722410702665004,0.6889333039258665,0.7051898328462721,0.7208463427918697,0.7357368725701509,0.7496956735417478,0.7625596194116508,0.7741712634155691,0.784382636698714,0.7930599004837093,0.80008907633257,0.805383271495582,0.8088914470497237,0.810607178754112,0.8105749957098343,0.8088933574434447,0.805713031632973,0.8012277960485743,0.7956600342508202,0.7892441944267365,0.7822086686878165,0.7747580747003207],[0.44862834363439114,0.44602062173517243,0.44380446426962006,0.4420400715279507,0.4407910962230427,0.44012424317230076,0.44010870419428105,0.440815394289801,0.442315949581492,0.4446814410795208,0.44798075102999285,0.45227855031839015,0.4576328062426605,0.46409174106291906,0.4716901620214405,0.4804451737282393,0.4903519741698231,0.5013821013827731,0.5134853830126482,0.5265933219124701,0.5406221599499128,0.5554753197835461,0.5710452853131174,0.5872150180608179,0.603859004694856,0.6208440259354093,0.6380297332807165,0.6552691178833842,0.6724089555147973,0.6892903128432734,0.7057492032583684,0.7216174854641351,0.7367241058677292,0.7508967986391892,0.7639643808852521,0.7757598282417055,0.7861244164389551,0.7949134008044095,0.8020038998762679,0.80730526944715,0.8107702538562417,0.8124029279672602,0.8122613057204917,0.8104565075953654,0.8071489868413954,0.8025377687141293,0.7968456322273144,0.7903033857686126,0.7831338757353957,0.7755375986730004],[0.44835673820764843,0.44573857895299684,0.4435119466980532,0.4417370273603764,0.4404774384727117,0.4397998219253496,0.4397732703306976,0.44046855281629615,0.44195710047255776,0.4443097053811003,0.44759488019953664,0.4518768181288561,0.4572128876302126,0.4636506003480605,0.4712240379391584,0.4799499408152639,0.48982429680322187,0.5008209457299145,0.5128928236123189,0.5259746553452952,0.539985747579738,0.5548323442092603,0.570409467711998,0.5866023014972276,0.6032871957579605,0.6203323824982884,0.6375984840548824,0.6549388982226819,0.6722001432383801,0.689222247828337,0.7058392757656285,0.7218800818745912,0.7371694093477552,0.7515294614003083,0.764782123897874,0.7767520999380182,0.7872713765470207,0.79618570959187,0.8033641003929337,0.8087118532585887,0.8121846236939724,0.8137960507251933,0.81361623564172,0.811766685627441,0.8084136867098644,0.8037572212442756,0.7980168161919726,0.7914170343251861,0.7841737205506032,0.7764824582310796],[0.44835704641626745,0.4457395901157028,0.44351313010129106,0.44173763082239226,0.44047643203574616,0.43979582996735844,0.43976449017130176,0.4404526578088999,0.4419311257490936,0.4442699152212043,0.44753661833977687,0.45179434849856376,0.45709924886023023,0.4634975370526174,0.4710221590700863,0.4796893707977884,0.4894959798359545,0.5004181813868482,0.5124123159385751,0.5254169013773913,0.5393550149086623,0.5541364605805583,0.5696595272546219,0.5858123236660477,0.602473743264893,0.6195141320792957,0.6367957386100348,0.6541730266990007,0.6714929342703706,0.6885951644678704,0.7053126022504805,0.7214719607578477,0.7368947810179685,0.7513989420693344,0.7648008975126996,0.7769189570374162,0.7875781008436737,0.796617064076115,0.8038987144867847,0.8093247769240262,0.8128530488717672,0.8145052155366432,0.8143606103590453,0.8125473513761361,0.8092335678184255,0.8046163933317149,0.7989090203624019,0.7923276983453094,0.785080068131861,0.7773559823974061],[0.4486153569616472,0.44600811885668074,0.4437906712512149,0.44202253276553394,0.4407665052326172,0.4400882394280905,0.44005563078706256,0.4407380112840685,0.4422050990669111,0.44452566329446574,0.4477658593930079,0.45198719315522,0.45724408908975067,0.4635810872891846,0.4710298054755373,0.4796060047905905,0.4893073257828849,0.5001122765556394,0.5119806576368671,0.5248550508314949,0.5386627556992403,0.5533176884258543,0.568721996802613,0.5847673167780358,0.6013356845145056,0.6183001567994459,0.6355252089773643,0.6528669872798456,0.6701734980059564,0.6872848226746209,0.70403345830511,0.7202448979983367,0.7357385929840169,0.7503294796880109,0.7638303238465556,0.7760552405929547,0.7868249047319983,0.7959741630612556,0.8033629570457864,0.8088915658092217,0.8125195115685131,0.8142734650399649,0.8142373657608806,0.8125412980756925,0.8093513724101764,0.8048587962046072,0.7992680784799335,0.7927855811783207,0.7856097186442825,0.77792376504695],[0.4491150678259555,0.4465257263832132,0.4443241058156595,0.44256904070114306,0.4413225223621022,0.44064924675093164,0.44061599158471004,0.4412907902504878,0.44274186674073834,0.4450362941562882,0.4482383413933023,0.4524074830919492,0.457596075395156,0.4638467583848941,0.47118974956848453,0.47964033441878373,0.48919697189639016,0.4998403878593123,0.5115337667829057,0.5242238146259341,0.5378422796767284,0.5523075477233769,0.5675260661723458,0.5833934863446452,0.5997955031058586,0.6166084213228664,0.6336995051005804,0.6509271806153141,0.6681411740673326,0.6851826772580956,0.7018846477610938,0.7180723718271086,0.7335644501964882,0.7481744155283173,0.7617132621947645,0.7739932711818267,0.7848336454691955,0.7940686199870934,0.8015588323127782,0.807206658390347,0.8109734600494928,0.812886096271865,0.813027757791333,0.8115258438338229,0.8085408829577663,0.8042556323600999,0.7988642011215924,0.7925619605692438,0.7855373042629668,0.7779661079822225],[0.44983741499687224,0.4472716850138472,0.4450905610716087,0.44335194743747786,0.44211674761304137,0.44144839387761725,0.44141220706601386,0.4420745565172566,0.44350178865448414,0.44575889380941464,0.4489078873400146,0.4530058973279394,0.458102983966047,0.4642397727419547,0.47144506646906303,0.4797336919699619,0.48910488547355513,0.4995414629584829,0.5110098447088438,0.5234607884977863,0.5368305493744745,0.5510421730938033,0.5660067045216561,0.581624187837284,0.5977844140286164,0.6143674244506029,0.6312438125733206,0.6482748876181784,0.6653127801916914,0.6822005860447223,0.6987726634032866,0.7148552253954409,0.7302674057539041,0.7448230275063177,0.7583333748095582,0.7706113588060812,0.7814775726430966,0.7907688204997196,0.7983496732086666,0.8041269017627359,0.8080633101849375,0.8101825954608505,0.8105625493154677,0.8093236274613257,0.8066175245786565,0.8026163579008113,0.797502507710799,0.7914596190217024,0.7846655663543145,0.7772881570718656],[0.45076204120331337,0.44822363275818256,0.4460655090798874,0.4443443970130578,0.44311983910137526,0.4424537063459649,0.4424095444276287,0.44305172673478754,0.44444438801720426,0.44665011638684826,0.44972839125569924,0.45373377426666944,0.45871389352046943,0.46470731086318573,0.4717414231848049,0.47983060340740386,0.4889748024578764,0.4991587793433573,0.5103520043043402,0.522509137603212,0.5355708872056048,0.5494650243060641,0.5641073728356919,0.579402653278987,0.5952451244211518,0.6115190168706351,0.6280987885937626,0.6448492593010327,0.6616257021971075,0.6782739926227688,0.6946309370776781,0.7105249362396355,0.7257771749077319,0.7402035827874291,0.7536178733134187,0.7658360384191402,0.7766827357330358,0.785999988676895,0.7936583312172683,0.7995694288879939,0.8036967479396053,0.8060591865366079,0.8067261717141514,0.8058078964224932,0.8034444579822576,0.7997954248343352,0.7950303346321288,0.7893205878624003,0.7828333407097918,0.7757280233234842],[0.451867576243219,0.4493582346423738,0.44722351901025786,0.4455187383766755,0.4443018140648072,0.44363277906111837,0.4435731164992705,0.4441849147033793,0.4455298185241393,0.4476677627714212,0.4506554854796162,0.4545448389635701,0.45938094700677634,0.46520029634399185,0.47202889340955284,0.47988064860566126,0.48875615018056157,0.49864194383839916,0.5095103479748965,0.5213197368369827,0.5340151513527203,0.5475290710308491,0.5617821971520481,0.5766841394908832,0.5921339475271051,0.6080204714029821,0.6242225742571953,0.6406092471469524,0.6570397035419822,0.6733635556210945,0.6894212023097268,0.7050445916530382,0.7200585594282884,0.7342829919185776,0.7475361096700348,0.7596392077573696,0.7704231813609416,0.779737026111172,0.7874580417601648,0.7935024268128006,0.7978335106008363,0.8004645207071508,0.801454986823006,0.8009027649919955,0.7989343669590439,0.7956953177653869,0.791341404863732,0.7860313785745153,0.7799216231172271,0.7731632857801911],[0.45313220304394064,0.4506518204343489,0.4485389732810417,0.44684732615148554,0.4456329392534185,0.4449537591857756,0.44486895671175075,0.4454380934154347,0.4467201028321395,0.4487720791001622,0.4516478788431892,0.4553965611636103,0.46006071657181186,0.46567476618642945,0.4722633413981969,0.4798398709169911,0.48840549495418534,0.4979483888214896,0.5084435161012217,0.5198527628209988,0.5321253506336083,0.54519840296456,0.5589975442605419,0.5734374397681792,0.5884222200963232,0.6038457725145833,0.6195919154006715,0.635534502941707,0.6515375355624389,0.6674553797219892,0.6831332306968811,0.6984079850749249,0.713109725845035,0.7270640593165673,0.7400955710768452,0.7520326676248046,0.7627139984584018,0.7719964302585351,0.7797640584016732,0.7859369561958045,0.7904776113146734,0.7933930952024266,0.7947323904703066,0.79458000834435,0.7930477484388294,0.7902661518998734,0.78637665234624,0.7815250823837447,0.7758570312682922,0.7695153717886826],[0.4545341876989278,0.45208097410424264,0.44998671997364076,0.448303238397065,0.4470845146801943,0.44638619404405955,0.4462649261044706,0.44677755235374855,0.4479801275687148,0.44992677414957655,0.4526683807476558,0.45625117362110623,0.46071521030657264,0.46609286778615977,0.47240741619893173,0.4796717771191704,0.487887555689717,0.49704440586686294,0.5071197424630691,0.5180787641946816,0.5298747122382472,0.5424492684036756,0.5557329979611081,0.5696457600350135,0.5840970362902147,0.5989861601928097,0.6142024607105319,0.629625364642228,0.6451245311764855,0.6605601217894592,0.6757833390605857,0.6906373993304394,0.7049591343184667,0.7185814402484059,0.7313367976984316,0.7430620485066782,0.7536044990303699,0.7628291689309479,0.7706265833400973,0.7769199775553474,0.7816704226619108,0.7848785942690903,0.7865827994844827,0.7868539462238355,0.7857887355941895,0.783502350549952,0.7801216185875529,0.7757793318441945,0.7706101690877456,0.7647483262242677],[0.4560523566354726,0.45362305675403714,0.4515426422295303,0.4498608917543588,0.44862953190923677,0.4479017276218906,0.4477314404795667,0.4481726451429545,0.4492783993244691,0.45109977087714603,0.45368463691619887,0.4570763844646444,0.4613125587999278,0.4664235219940172,0.4724311961096983,0.4793479683732784,0.4871758255098398,0.4959057605090962,0.5055174611389951,0.5159792532384229,0.5272482420588513,0.5392705782467924,0.5519817736540618,0.5653070041186756,0.579161357566601,0.5934500120416641,0.6080683565785981,0.6229020966950617,0.6378274153187745,0.6527112892573104,0.6674120906033263,0.6817806302966751,0.6956618237112,0.7088971681168227,0.721328206005777,0.7328010858232552,0.74317219496129,0.7523146040094386,0.7601247325446551,0.7665283103282136,0.7714845501557269,0.7749876666697515,0.7770654735109578,0.7777754927483523,0.7771994735073816,0.7754373201891979,0.7726012898281952,0.7688110881917922,0.7641902242375234,0.7588636017647452],[0.45766650915156337,0.45525665106138935,0.45318413305640937,0.4514965436078064,0.45024319883163094,0.44947464130443276,0.44924201857155044,0.4495963351127357,0.45058757687397616,0.452263715126652,0.4546696064670042,0.45784581781271183,0.46182741811127165,0.4666427900271652,0.47231252219245917,0.4788484425784309,0.4862528440071441,0.49451793379297676,0.5036255138636508,0.5135468706835358,0.5242428318017708,0.5356639324735308,0.5477506335494965,0.5604335400515073,0.5736335862293229,0.5872621746732909,0.6012212819739694,0.6154035700283067,0.629692569601391,0.6439630305281171,0.6580815598139989,0.6719076923441737,0.6852955540894674,0.6980962764044243,0.710161289881846,0.7213465511529382,0.7315176199870322,0.7405553018849746,0.7483613282508823,0.7548633372500031,0.7600183605876999,0.7638142092320779,0.7662685633985225,0.7674260499005641,0.7673539409448016,0.7661372394806806,0.7638738574396872,0.7606704180935595,0.756638960400047,0.751894491145364],[0.4593577583458595,0.45696192097098404,0.4548904705985024,0.4531886784193867,0.45190333110874137,0.45108224306165806,0.4507736604286064,0.45102555365069746,0.4518848003827652,0.45339626765488683,0.45560181074177253,0.45853921594170516,0.46224112420402685,0.46673398058321564,0.4720370587369614,0.4781616081215658,0.4851101629946756,0.4928760371701637,0.5014430088705064,0.5107851796148606,0.5208669739181375,0.5316432359399836,0.5430593768076345,0.5550515321258932,0.5675467019333713,0.5804628633169102,0.5937090674093503,0.6071855562999744,0.620783960503206,0.6343876629911591,0.6478724396527288,0.6611075052502766,0.6739571032155443,0.6862827689885114,0.697946359569635,0.7088138653201332,0.7187598966444259,0.7276725736163117,0.7354583700786934,0.7420463330494985,0.7473910851992149,0.7514741685450952,0.7543035778767028,0.7559116670657479,0.7563518754669818,0.7556948462058393,0.7540244899477013,0.7514344187668455,0.7480249668126862,0.7439007607188332],[0.4611087976606734,0.45872088514907383,0.4566430942413389,0.4549182811033307,0.45359061633632614,0.45270511497117055,0.4523070702325014,0.452441390128303,0.453151840763786,0.4544802064320814,0.45646538376309365,0.4591424349469572,0.46254163232605733,0.46668753214942055,0.47159811752305286,0.4772840482909137,0.48374804813665806,0.49098444707049815,0.4989788823165538,0.5077081450089952,0.517140146877862,0.527233972633925,0.5379399814345024,0.549199924894872,0.5609470589832437,0.5731062417172719,0.5855940267053596,0.5983187832030392,0.6111808955022789,0.6240731169231738,0.636881174490487,0.6494847362829557,0.6617588593006118,0.6735760243153809,0.6848088270389809,0.6953333245514909,0.7050329302753594,0.7138026195739527,0.7215530780357594,0.7282143382393369,0.7337384533121645,0.7381008701788875,0.7413003726493224,0.7433577041279561,0.7443131789748555,0.7442236995791597,0.7431595987810788,0.7412016377153072,0.7384383342279139,0.734963616819799],[0.46290409372340496,0.46051760650384965,0.4584257859322291,0.4566690043862479,0.45528876089950227,0.4543272324458493,0.45382674052680577,0.45382913393895197,0.4543750929934926,0.45550336578270545,0.4572499530542427,0.4596472643289452,0.46272327328171264,0.4665007040984151,0.47099628149025474,0.47622007448182724,0.48217495770519675,0.4888562041947596,0.49625121184283166,0.5043393535851879,0.513091931059491,0.5224722046541095,0.5324354706480943,0.5429291588981772,0.5538929319865211,0.5652587782480437,0.5769511058527637,0.5888868623293494,0.6009757227472322,0.6131204091315333,0.6252172218124127,0.6371568773861208,0.6488257532499639,0.6601076290458969,0.6708859837399175,0.6810468478645676,0.690482123429924,0.6990931789038929,0.706794425796847,0.7135165186272725,0.7192088220109061,0.7238408711490658,0.7274027009171382,0.7299040942084942,0.7313729530916065,0.7318530884555075,0.7314017389772155,0.7300870736787205,0.727985825439452,0.7251810806779108],[0.4647300088798796,0.4623383029043042,0.46022476394169914,0.4584272398088299,0.45698453188875243,0.4559359704313689,0.4553209160476945,0.45517818963481443,0.45554543687279664,0.45645843796641444,0.4579503781722658,0.4600510993827861,0.4627863569898464,0.4661771086762881,0.4702388619667719,0.4749811048030159,0.48040683798531514,0.4865122204619374,0.4932863291019246,0.5007110250901934,0.5087609108896685,0.5174033560957128,0.5265985683252097,0.5362996868956338,0.5464528823677749,0.5569974536572596,0.5678659258375964,0.5789841654097106,0.590271545123862,0.601641206663057,0.6130004854078852,0.6242515749471872,0.63529251640517,0.6460185937900992,0.6563241950579983,0.6661051538250743,0.6752615173655878,0.6837005999132691,0.691340094305883,0.6981109554949919,0.7039597609920459,0.7088503074753874,0.7127643102694333,0.7157012050823011,0.7176771732914153,0.7187235930467174,0.7188851431940113,0.7182177570647267,0.7167865547091078,0.7146638022742167],[0.4665748588089146,0.4641713862118742,0.46202869815979575,0.4601821036627474,0.4586677077265051,0.45752201264290693,0.45678145559888467,0.4564818858183963,0.4566579878654339,0.4573426615505982,0.4585663728239304,0.4603564937009024,0.46273665214977094,0.4657261144157309,0.4693392219751293,0.47358490288713045,0.4784662727265962,0.4839803338984016,0.49011777466848216,0.4968628616731249,0.5041934130338772,0.5120808344377508,0.5204901982909182,0.5293803466214424,0.5387040017735215,0.5484078748589281,0.5584327700697075,0.5687136929823842,0.5791799826357257,0.5897555001985675,0.6003589210396589,0.6109041909629841,0.6213012190606648,0.6314568849279991,0.6412764305810058,0.650665279985778,0.6595312766849757,0.6677872551633156,0.6753537784485727,0.682161807121995,0.6881550386232627,0.6932916844775661,0.697545531769739,0.7009062414535356,0.7033789399922808,0.7049832364743518,0.7057518305732973,0.7057288673469124,0.7049681548865778,0.7035313102874218],[0.46842891197577435,0.46600743800903827,0.46382865711200527,0.46192534998164114,0.46033095163179644,0.4590791799785259,0.45820361004317867,0.457737197658029,0.45771175951003423,0.45815741954339506,0.45910203491505414,0.46057061752633544,0.46258476924416747,0.4651621498714539,0.4683159963863756,0.4720547097516892,0.47638152172829384,0.48129424890613104,0.48678513512942023,0.49284077734992215,0.4994421244446269,0.506564534348044,0.514177872443305,0.5222466337516382,0.5307300730431072,0.5395823303865963,0.5487525446350943,0.5581849537494623,0.5678189887408152,0.5775893776719752,0.5874262881481701,0.597255551523083,0.6069990292846056,0.6165751992020299,0.6259000494794267,0.6348883628877511,0.643455438102063,0.6515192272667704,0.6590027773324554,0.6658367748219896,0.6719619420950078,0.6773310388334722,0.6819102833738507,0.6856801025384378,0.6886352159716724,0.6907841367609363,0.6921482111270222,0.6927603256420436,0.6926633901791578,0.6919086736961876],[0.4702843385224884,0.46783913110536784,0.46561799737126874,0.46365122293386263,0.4619696219688732,0.46060419382795426,0.45958573372965095,0.4589444018435753,0.4587092576132675,0.4589077688089384,0.4595653073502146,0.4607046461203684,0.4623454725028393,0.46450393491060293,0.46719223791272263,0.47041829957262654,0.4741854813474327,0.47849239659085385,0.48333279875527524,0.4886955453126709,0.4945646287438726,0.5009192621460997,0.5077340043980845,0.5149789085333693,0.5226196769605596,0.5306178082687921,0.5389307223832219,0.5475118537322229,0.556310706115268,0.5652728689140104,0.5743400036827431,0.5834498251627196,0.592536123500077,0.6015289049685553,0.610354761349849,0.6189375990055813,0.6271998458796629,0.6350641903756594,0.642455794432111,0.6493047990844291,0.65554885431322,0.6611353898452885,0.6660233985260732,0.6701845998710144,0.673603952643937,0.6762795655231131,0.6782221024170983,0.6794537944956259,0.6800071631477133,0.6799235390086962],[0.47213511660434654,0.46966110614958734,0.4673922060846446,0.46535626076442965,0.46358153305934463,0.46209638925774316,0.46092894568277615,0.4601066815886877,0.45965602505708547,0.4596019208043803,0.4599673908567133,0.4607731007303896,0.46203694484002295,0.4637736651243955,0.46599451616689275,0.4687069883216763,0.471914597588776,0.4756167473921972,0.4798086632995908,0.4844813974445593,0.4896218953451279,0.4952131142666213,0.5012341794506459,0.50766056247432,0.51446426462305,0.5216139872662083,0.5290752706228414,0.5368105819465973,0.5447793343834761,0.5529378196349399,0.5612390433463013,0.5696324656527224,0.5780636756865204,0.5864740724295726,0.5948006831011521,0.6029763074343156,0.6109301957129122,0.6185894096346389,0.6258808691112544,0.6327339051701941,0.6390830036049415,0.644870392074858,0.6500481883611002,0.6545799415502467,0.6584415123938024,0.6616213259211344,0.6641200807234967,0.6659500194674312,0.6671338636938158,0.667703503465617],[0.4739769042543667,0.4714698125822986,0.46914870704460504,0.4670390629297834,0.46516667930939737,0.46355739210720426,0.4622367557359045,0.4612296979789512,0.46056015462440436,0.4602506921685074,0.4603221285474505,0.46079316315254465,0.46168002815666737,0.4629961732665691,0.46475199530038147,0.46695462242803965,0.469607760548974,0.47271160625268316,0.47626282732602465,0.4802546080910721,0.48467675323023474,0.48951584037886875,0.49475540874223856,0.5003761683052341,0.5063562117110157,0.512671208362009,0.5192945575038792,0.5261974738781515,0.5333489762321407,0.5407157466082719,0.5482618294210588,0.555948148804102,0.563731848724168,0.5715655133467413,0.5793964113781088,0.5871660137743837,0.5948101065054118,0.6022597772939552,0.6094433564986307,0.6162891129765995,0.6227282992651937,0.6286981015424681,0.6341441501306678,0.6390223975715211,0.6433003056956047,0.6469573750226948,0.6499851003353432,0.6523864558274198,0.65417501328023,0.6553737870009263],[0.4758068846686838,0.47326332281472533,0.4708866402073507,0.46870003135268085,0.4667269345980561,0.464990772945017,0.4635146695486031,0.46232114259215684,0.46143178577551536,0.46086694214967105,0.4606453803476177,0.4607839832602758,0.4612974597491155,0.46219808995248185,0.46349551404710854,0.46519657294085465,0.46730520733271397,0.4698224189808259,0.472746295017762,0.4760720929177939,0.4797923804154055,0.48389722141233305,0.4883743957256289,0.49320963735418544,0.49838687260332204,0.5038884356495738,0.5096952346630463,0.5157868362221841,0.522141429528412,0.5287356256072758,0.5355440424545745,0.5425386299529589,0.5496877083407059,0.5569547480519562,0.5642970275273603,0.5716644718616615,0.578999136006479,0.586235800045858,0.5933038685606822,0.6001303233200496,0.606643166621731,0.612774773030802,0.6184647448544316,0.6236620754796719,0.6283265788497093,0.6324296332432193,0.6359543305975881,0.6388951369173098,0.6412571676310126,0.6430551725604923],[0.4776235924200225,0.4750411279825865,0.4726066238630179,0.47034109586140893,0.4682657378468278,0.466401689659048,0.46476978513564027,0.46339028489224654,0.4622825997921396,0.46146501227487635,0.4609544037698359,0.4607659971877403,0.4609131238537483,0.46140702412764734,0.46225669028804783,0.46346875901705215,0.4650474590348402,0.4669946171687857,0.46930972350003963,0.4719900533244257,0.4750308405918219,0.4784254943039844,0.48216584604228585,0.48624241326638956,0.490644659084413,0.495361224577035,0.5003801041483585,0.5056887274842948,0.5112739033953044,0.5171215714204601,0.5232162979541005,0.529540448653919,0.5360729773160149,0.5427878138304882,0.5496519482248912,0.5566235358647169,0.5636506517814942,0.5706714475073111,0.5776160856816231,0.5844100928087042,0.5909783011745119,0.5972486185234602,0.6031551853120467,0.6086407572936423,0.6136583111420896,0.6181719456669315,0.6221571801191922,0.625600757274897,0.6285000541949359,0.6308621940343149],[0.4794267275759639,0.4768039229544308,0.4743105078470337,0.4719654329145075,0.46978777458458887,0.46779652921087744,0.46601039217245943,0.4644475264282199,0.463125326142894,0.4620601820184462,0.4612672558094126,0.4607602720850879,0.4605513355399235,0.460650781974924,0.4610670704292786,0.46180672281498536,0.46287431581287236,0.4642725277706208,0.46600224096628867,0.4680626969322373,0.4704516996258669,0.47316585809942097,0.47620085691921105,0.4795517388030555,0.48321317959644994,0.4871797305361226,0.4914459964465989,0.4960067107617156,0.5008566588013119,0.5059903895188873,0.5114016434840801,0.5170824131534264,0.5230215465080876,0.5292028241677119,0.5356025295963898,0.5421867898458469,0.5489094634223796,0.555711766645879,0.562524346179681,0.5692712151791619,0.5758742769217308,0.5822574809200902,0.5883502047507276,0.5940897794462386,0.5994232097763749,0.6043081865882971,0.6087135001962245,0.6126189621386835,0.6160149352147981,0.6189015620357778],[0.4812169640656278,0.4785533875120766,0.47600112528716587,0.4735771856837257,0.47129866316213787,0.46918255780182017,0.4672455839394843,0.4655039723568571,0.46397327130850813,0.4626681525158232,0.46160222892570785,0.4607878914699313,0.4602361721950387,0.45995664090677946,0.4599573418478073,0.4602447758858952,0.46082393223763907,0.46169837191468766,0.4628703628920903,0.46434106449644913,0.46611075571390426,0.46817909901127885,0.47054542778856184,0.47320904162191885,0.4761694888381373,0.47942681045203217,0.4829817128215167,0.486835628232853,0.49099061273707956,0.4954490187098153,0.5002128657924347,0.505282818615684,0.5106566651765235,0.5163271841735719,0.5222793259553927,0.5284868350699788,0.5349091151286316,0.5414901619687206,0.5481609251644665,0.5548440468408306,0.561458978924449,0.5679264205631349,0.5741718214656869,0.5801279789170681,0.5857368267633399,0.5909505282838949,0.595731983333553,0.600054853636251,0.603903201567956,0.6072708284562849],[0.48299575793648375,0.48029196979982924,0.4776820494371389,0.47518119250021273,0.4728046530797024,0.47056758738455257,0.46848489033555457,0.4665710292580616,0.4648398796368982,0.46330456857963975,0.46197733216417886,0.46086939316334774,0.45999086568780717,0.4593506930216705,0.45895662430984535,0.45881523477375663,0.4589319927804632,0.45931137537885613,0.45995703186072634,0.4608719925150428,0.46205891701633406,0.4635203737909341,0.4652591381692351,0.4672784930447832,0.4695825109624967,0.4721762908457584,0.4750661157094245,0.47825948943919483,0.4817650007981691,0.4855919510323933,0.4897496676414764,0.49424641103964917,0.49908776323963167,0.5042743697783594,0.509798896376386,0.5156421269897307,0.5217687297075208,0.5281252405282137,0.5346429391191801,0.5412435695573397,0.5478449016871331,0.5543652839569276,0.5607271771756631,0.566859779411917,0.5727008611103285,0.5781979245838196,0.5833087947981599,0.5880017402944198,0.5922552145573986,0.5960572994498752],[0.48476516039967965,0.482022677285199,0.4793573611792515,0.4767827295833389,0.4743123416859413,0.4719596651285731,0.4697379389407569,0.4676600366326627,0.46573833408307364,0.46398458741431564,0.4624098264555164,0.461024269611409,0.4598372659294495,0.45885726985349795,0.45809185353737464,0.45754776064668756,0.45723100429299923,0.4571470101182907,0.4573008035791756,0.457697238162932,0.4583412585805613,0.45923818988217285,0.46039403985354094,0.46181579787147475,0.46351170847589834,0.4654914920823818,0.46776647831057466,0.47034960913089713,0.4732552592290821,0.4764988094760505,0.48009589603421154,0.4840612423574729,0.488406964150569,0.4931402183234666,0.4982600463536191,0.5037532437351315,0.5095892867835291,0.5157171487703555,0.5220689089923275,0.5285663166205207,0.5351264832055731,0.5416664269178861,0.5481066020723364,0.5543735434157857,0.5604017448716453,0.5661348835214408,0.5715264911564526,0.5765401674246383,0.5811494203266853,0.5853372116458598],[0.4865276398002192,0.48374887960862956,0.48103143180556474,0.47838727288679006,0.47582841430573863,0.4733667911242549,0.47101414965563704,0.46878193787907085,0.4666812029416122,0.4647225005070238,0.4629158210180003,0.46127053806744595,0.45979538398574504,0.45849845740938955,0.45738726697346815,0.4564688143450384,0.4557497185712204,0.4552363821433779,0.4549351972647002,0.4548527885339212,0.4549962855911344,0.4553736161617236,0.4559938063063055,0.4568672704360337,0.45800606865417326,0.4594241030832563,0.461137217862123,0.4631631592719036,0.46552134280401875,0.46823236276638835,0.471317167120117,0.47479580557570816,0.4786856425309128,0.48299890821880576,0.48773944149544024,0.49289845609284016,0.49844924178510963,0.5043435283703604,0.5105153104967398,0.5168875478492336,0.5233778246105593,0.5299028760981215,0.5363821244983147,0.5427403523772667,0.5489096313867228,0.5548306137356872,0.5604532850117814,0.5657372684564121,0.5706517626502791,0.5751751867090322],[0.4882859158865903,0.48547412684192404,0.4827087247280256,0.4800002828301848,0.47735941167360985,0.474796668306955,0.47232246700616526,0.469946994958253,0.4676801369239044,0.4655314132247039,0.46350993561892856,0.461624385682806,0.4598830201669152,0.4582937074183854,0.4568639983212829,0.4556012342870809,0.45451269360476093,0.453605775917433,0.4528882227084885,0.45236836942765185,0.4520554222267452,0.45195974915139914,0.452093171973702,0.4524692405558329,0.45310346658914813,0.45401348762209476,0.45521912532666836,0.4567422938055622,0.4586067042651052,0.4608373014427972,0.46345935467967064,0.4664971124022546,0.4699719130322928,0.47389962823882975,0.4782872982229159,0.4831288317122625,0.488400080023506,0.4940560742702309,0.500034032646123,0.5062593741564538,0.5126512903497737,0.5191272703365691,0.5256066597143371,0.532013376076252,0.5382778961749191,0.5443386198157305,0.5501427061798665,0.5556464695875913,0.5608154135642825,0.5656239743713605],[0.49004280900941477,0.48720198584098073,0.48439361883881915,0.4816270146534397,0.478911527407928,0.4762564873193778,0.4736711328046545,0.47116454940304375,0.4687456192013016,0.4664229847087938,0.46420503126986357,0.4620998920851039,0.46011547971144484,0.458259547493547,0.4565397837190323,0.4549639403631164,0.4535399970711806,0.4522763594970513,0.45118208924341885,0.4502671604052527,0.44954273505361736,0.44902144685870604,0.4487176783642179,0.44864781310058627,0.4488304386559588,0.4492864708920776,0.45003916256967175,0.4511139516065312,0.4525380949129066,0.45434002314394534,0.4565483397592291,0.45919037467312346,0.4622901894469358,0.4658659216034553,0.46992637113261027,0.47446688121308245,0.47946525479641877,0.4848798910593667,0.49065200862896663,0.4967105601919219,0.5029774218432412,0.5093718478488651,0.5158140456361908,0.5222279388890358,0.5285432198395674,0.5346967906183075,0.540633686116683,0.5463075625859631,0.5516808282036152,0.5567244842766349],[0.49180110616454287,0.4889358965827264,0.48609025535864925,0.4832723561519866,0.4804904371769142,0.47775274782869825,0.4750675005218968,0.47244283083945743,0.46988676936797436,0.46740722878098445,0.46501200980093904,0.4627088295924668,0.46050537588597085,0.4584093896737412,0.4564287786340455,0.45457176249643755,0.45284705033813344,0.4512640482694825,0.4498330940952298,0.44856571329006273,0.4474748879555617,0.44657532727368676,0.44588372426927986,0.44541897935780383,0.4452023660903848,0.44525760861442715,0.4456108335427452,0.4462903510795915,0.4473262113436006,0.44874947192429965,0.4505911021834209,0.45288043992032617,0.4556431107891436,0.4588983334806809,0.4626556069558651,0.4669110275382629,0.4716440782535625,0.47681637636739155,0.4823733577409551,0.48824817310028834,0.49436625249763866,0.5006495261405584,0.5070199497629808,0.5134022937821532,0.5197262554343667,0.5259279775047461,0.5319510587802395,0.5377471362777791,0.5432761125062822,0.5485060939927394],[0.4935634451250055,0.49067904963177245,0.48780240918666823,0.48494069363962317,0.4821011601988967,0.4792911166969145,0.47651789148224283,0.473788812798388,0.4711112007167515,0.46849237480946276,0.4659396807522233,0.4634605389112335,0.46106251766499556,0.45875343371472993,0.45654148091995983,0.4544353882320374,0.4524446060606042,0.4505795188665057,0.44885167989598285,0.44727406171571005,0.445861313529659,0.44463001310126815,0.4435988974032629,0.44278905180004224,0.44222403255685494,0.44192989169293156,0.441935066599412,0.4422700894290343,0.4429670631657639,0.44405884294246517,0.4455778537961695,0.44755447274542437,0.4500149117992597,0.4529785789523699,0.45645500963515756,0.4604407171323063,0.46491670328336204,0.46984760170261275,0.47518299603973213,0.4808605097247843,0.486809692206319,0.49295586734307817,0.49922350995366616,0.5055390081288528,0.5118328100459697,0.5180410087335856,0.5241064350766247,0.5299793312977431,0.5356176735434572,0.5409872066765791],[0.49533221728879284,0.492434285200589,0.48953338501401644,0.4866358061568105,0.48374795280407845,0.48087632238978123,0.4780274918677052,0.4752081143394104,0.4724249288102586,0.4696847858908265,0.46699469220624057,0.4643618760856502,0.4617938767530343,0.4592986587031675,0.4568847521968659,0.45456141982065856,0.4523388477994937,0.45022835919612,0.4482426442429871,0.44639600079262304,0.4447045751956673,0.44318659077150857,0.4418625473698312,0.44075537127678477,0.43989048984896745,0.4392957997382166,0.43900149143375833,0.43903968625363926,0.439443835288518,0.44024782413092567,0.4414847247273694,0.4431851411765191,0.4453751197641601,0.4480736538355894,0.4512899390923359,0.45502074068274556,0.4592484596279786,0.46394053654292494,0.46905051144536897,0.4745204990656503,0.4802844518544742,0.4862715741347892,0.49240946496955934,0.4986267885612722,0.5048554146952419,0.5110320456466604,0.5170993781926652,0.5230068605835634,0.5287111057986391,0.5341760196033225],[0.4971094893140682,0.4942040136573317,0.4912859377941363,0.488360787208246,0.48543423297823973,0.4825120841203612,0.4796002885331751,0.4767049449144912,0.47383232810696135,0.4709889303279364,0.4681815206297045,0.4654172246951874,0.46270362667764064,0.46004889421623685,0.4574619269770392,0.4549525280540684,0.45253159628957734,0.45021133600558233,0.44800547874669305,0.44592950938051146,0.4440008862466387,0.44223924194744685,0.4406665477943302,0.43930722083336154,0.43818814777019394,0.4373385950449315,0.4367899689290669,0.43657538419155506,0.4367289953741751,0.4372850425589903,0.4382765666639835,0.4397337632337264,0.44168197767368045,0.4441394120391223,0.4471147249875769,0.45060485224838526,0.45459349366933005,0.4590506930769493,0.4639337080106466,0.46918901720857986,0.4747550499487081,0.48056516497789314,0.4865505104430409,0.4926425460963406,0.4987751318649288,0.5048861649145497,0.5109187895471174,0.5168222240168396,0.5225522556071142,0.5280714560941377],[0.4988969431266768,0.49599015680508735,0.493062216585513,0.4901179926844571,0.4871625341225439,0.4842010734727882,0.4812390408115039,0.4782820889924752,0.47533613239808475,0.47240740126786174,0.46950251354504446,0.4666285658936193,0.4637932450992733,0.4610049604541353,0.4582729969123442,0.45560768776547944,0.4530206042963439,0.450524758297498,0.4481348114567304,0.4458672833836935,0.4437407474492462,0.44177600060480415,0.43999618992733497,0.4384268748041039,0.43709599948324757,0.4360337463102177,0.4352722356394314,0.434845034724337,0.4347864358994411,0.43513046594345556,0.4359095968211152,0.43715314802296723,0.43888540925565417,0.44112357592692564,0.443875678790341,0.4471387848906708,0.45089780340057284,0.45512518753509174,0.4597816595688509,0.4648178579748056,0.470176623000586,0.47579557227531477,0.48160966175526576,0.48755352214636827,0.49356345578856553,0.49957905040407025,0.5055444115631611,0.5114090411587018,0.5171284015245372,0.5226642093672824],[0.5006958334710465,0.49779410881012776,0.49486373030189307,0.49190901310462964,0.4889344857060427,0.48594490565038106,0.48294528483719823,0.4799409262611718,0.4769374740470106,0.4739409785323427,0.4709579779455296,0.4679955978943176,0.46506166940375326,0.46216486559544195,0.45931485626163715,0.4565224785324702,0.4537999205376498,0.45116091339939796,0.44862092503572015,0.4461973470786218,0.44390966370196233,0.44177958830039255,0.4398311507771092,0.43809071473449956,0.43658690023464386,0.4353503842353746,0.43441354772990837,0.4338099367493345,0.4335735049363716,0.4337376102895221,0.4343337507703863,0.43539004655697683,0.4369295147761595,0.4389682372888991,0.44151358829504544,0.444562748323751,0.44810175363899646,0.45210528443762604,0.4565372765714517,0.46135228702880654,0.46649741436397224,0.47191451588796235,0.4775424763536041,0.4833193400232231,0.4891841868474842,0.495078693288986,0.5009483617445245,0.506743430295631,0.5124194903545475,0.5179378475265346],[0.5025069618370068,0.49961671529705176,0.4966913335238974,0.49373466791492115,0.49075081806220955,0.48774415704416835,0.48471936644623836,0.4816814827294006,0.4786359565056627,0.4755887261352084,0.47254630681259224,0.4695158959403252,0.4665054950774935,0.46352404807785397,0.46058159417466493,0.4576894337063819,0.4548603028863818,0.4521085524800591,0.44945032344543245,0.4469037105054728,0.4444889022482726,0.4422282837090866,0.44014648452055044,0.4382703527185129,0.436628831336874,0.4352527123206794,0.43417424053691983,0.43342654056747165,0.4330428417427072,0.43305548425047985,0.43349470338003465,0.4343872124677257,0.43575463952947835,0.43761191671898125,0.43996576886062,0.4428134830345551,0.446142145952044,0.4499284941007802,0.4541394347835983,0.4587331882402591,0.4636609081208517,0.46886858726996633,0.4742990537506424,0.4798938949347552,0.48559519548337293,0.4913470223388646,0.49709662821962636,0.5027953724495665,0.5083993754781686,0.5138699334787754]],[[0.13543102397796292,0.13182603445674745,0.12812197173835244,0.12434568413701097,0.12052925351786013,0.11670991868715876,0.1129296282105822,0.1092340873455703,0.10567116109375391,0.10228852446470435,0.0991305300117428,0.09623440418266534,0.09362608152160964,0.0913161991197428,0.08929692626649587,0.08754030600638467,0.08599858271541161,0.08460661461447391,0.08328604403604985,0.08195057550609358,0.08051159520716787,0.07888345854795391,0.07698799675036101,0.07475804577629967,0.07214000564545885,0.06909556460579709,0.06560277601964523,0.06165667858672044,0.057269627142846745,0.05247147162198661,0.04730970114761551,0.04184967444334851,0.036175115102816145,0.03038923266538092,0.02461735304625031,0.019013534730659164,0.013779126829844493,0.009222295122745723,0.00595129958946789,0.004968382191747059,0.005836202839849086,0.006795962623470127,0.0070463875127331965,0.006465466723469471,0.00540355921313035,0.005085102180396452,0.0070486224673486034,0.010887690164101455,0.01575568515594681,0.021257955207103583],[0.1328460340392906,0.12896816257381563,0.12497211545285596,0.12088615988019882,0.11674487617697367,0.11258937078215366,0.10846712725420521,0.10443131277813997,0.10053932506709118,0.09685036312610938,0.09342186824049618,0.09030484533861619,0.08753835761711239,0.08514385336549386,0.08312031592692752,0.08144134580863532,0.08005503913902762,0.0788869276058011,0.07784550629002758,0.07682930972986737,0.07573431676566501,0.07446066832667868,0.07291809656276894,0.07102988533475481,0.06873548403322816,0.06599204928061957,0.0627752242480974,0.059079433247529616,0.0549179125320577,0.0503226450921627,0.045344336112868665,0.04005257620648066,0.03453643274650365,0.02890600061686533,0.02329628898619588,0.017877438045505123,0.012884181479303142,0.008707973278707959,0.0061202541397840995,0.005904597428726382,0.007061262388317721,0.008110446674299134,0.008454582470320765,0.007993098299561562,0.006961218198697221,0.006134438580157628,0.006913272869716234,0.009798281173295372,0.014076597621850834,0.019189387499807493],[0.1303110772317582,0.12615375201067258,0.12185581001427863,0.11744621868205136,0.11296132739976139,0.10844545572879563,0.10395117810851896,0.09953908258111885,0.09527670347697938,0.09123626653775335,0.08749088878318964,0.08410902007798358,0.08114727638323815,0.07864240840967676,0.07660382687785212,0.07500852703533713,0.07380003605421372,0.07289203572352056,0.0721759647150155,0.07153085130024678,0.07083334568805867,0.06996637978332426,0.06882567705237957,0.06732404921776697,0.06539384631946332,0.06298807766212851,0.06008069439823944,0.056666422929022874,0.052760429994676006,0.04839802058983533,0.043634538152931224,0.03854567822031275,0.03322860766138673,0.027804791822043463,0.02242683905861966,0.01729570989248504,0.012705973513852505,0.009154109919770833,0.007398393037647159,0.007661098449875821,0.008852540120648681,0.009902302383707897,0.010344673816581008,0.010081407502686636,0.00926891173464772,0.008380285796117354,0.00830804067603572,0.009915812529758252,0.01319463330348908,0.017646364848904427],[0.12786243541798703,0.12342342004041733,0.11881811149887636,0.11407525161641632,0.10923192300562341,0.1043345814588668,0.09943990999164032,0.0946152583314771,0.08993829921602575,0.08549537679031764,0.08137789585132678,0.07767612431712843,0.07447014458814855,0.0718185617028658,0.06974687904455351,0.06823861537506908,0.06723231732941577,0.06662605047079323,0.0662883414830747,0.0660724403127979,0.06583033299731303,0.06542401818669104,0.06473314747459283,0.06365933881447683,0.062128025158552175,0.06008875379121742,0.05751466898252428,0.054401681518795215,0.0507676442622313,0.04665174220723164,0.04211427766988092,0.0372371102227997,0.03212528021322987,0.02691104990577717,0.021763426461588478,0.016910954662934668,0.012695310110800242,0.009662098195784749,0.008450991218526932,0.008969411095268831,0.010203982846410284,0.011298698510499057,0.011859891022355344,0.011784164409379069,0.01116473649150317,0.010304086022610447,0.009788365696110874,0.010413604018506805,0.012652495782756387,0.016336034936180913],[0.12553968487819647,0.12082221264611173,0.11590993997908891,0.11083028908844716,0.10561974715870802,0.10032536834658617,0.09500629564826424,0.08973510409773854,0.08459858870079211,0.07969734991494781,0.07514318519629422,0.07105300692136196,0.06753810979368688,0.06468863602735957,0.06255538131108782,0.06113396884225503,0.060357731802376774,0.0601032360714367,0.06020696341618416,0.06048710045632815,0.06076375294368101,0.06087362067583654,0.06067845938973011,0.060068634681615815,0.058963581690657706,0.05731068192983232,0.05508355565056675,0.05228033682762809,0.04892222188703546,0.04505244846237218,0.04073584420248866,0.03605919899626947,0.031133046536145063,0.026096269783790916,0.02112702327652574,0.016468531098757375,0.012486701178817049,0.009748515174524958,0.008832249604579743,0.00952314589755021,0.010846529272808126,0.012036113131693399,0.012733471189013662,0.012827145284051255,0.01236193105615922,0.011533395502845517,0.010748961013970174,0.010682199078395186,0.012030709416628026,0.01498541773872388],[0.12338478268080952,0.11839866885669774,0.11318720004017488,0.10777530732725135,0.10219734429625252,0.09649900971649557,0.09073954379630057,0.0849941098099154,0.07935609468670407,0.07393871277991453,0.06887469391652774,0.06431198724151821,0.06040267504671644,0.05728275400248424,0.05504378792376747,0.053703999366739336,0.05319191276464885,0.05335280713066109,0.053976115788569326,0.054830872768436754,0.05569576833469503,0.05637771976314976,0.05671986263397222,0.056602698363307245,0.05594188244515955,0.05468489643627999,0.052807752496473404,0.05031220310425508,0.04722359315252801,0.04358937108462107,0.03947829240351801,0.03498049444155408,0.030208985287320085,0.025303968344180666,0.020443650565671146,0.01587083941414812,0.011955314984187015,0.009287404916654574,0.008486255730865836,0.009317846863288506,0.01077010428692013,0.012087627764553561,0.012926552405912338,0.013169058414080951,0.012824575131869862,0.012015465987591149,0.011032772787388383,0.010447201723744946,0.011070808401046992,0.013414961855503083],[0.12144076926028123,0.11620337427430423,0.1107092357068901,0.10497969466736098,0.09904540114412974,0.09294851209693679,0.08674541914337466,0.0805100969087768,0.0743380710395664,0.06835071542937078,0.06269886944897922,0.05756327459456967,0.05314691633709053,0.049652200441523464,0.047238327163321055,0.04596713715397284,0.045764680480453505,0.04642722818012143,0.04767090372764377,0.049193836600184865,0.050721611440559304,0.05202839560509404,0.052940767234947055,0.053333356814275375,0.053122174493188304,0.05225829983301999,0.05072278378138253,0.048522822567368756,0.04568900990654682,0.042273454563867496,0.0383486365822746,0.03400705180013021,0.029362050110295437,0.024551102459065017,0.019744911712637557,0.015171919363887369,0.011183482031326922,0.008387063380257279,0.0075429496192692975,0.008488202109114424,0.01008743149224813,0.011538119694010756,0.012504151736017136,0.01286815473555999,0.012615592923913666,0.011814319451144924,0.01066801491162144,0.009661517198382399,0.009689474544686365,0.011575997027978353],[0.11975008997213153,0.1142869725982889,0.1085365254838916,0.10251567475176084,0.09625004236876962,0.08977618524184816,0.0831445377822445,0.07642334486737247,0.06970395749981557,0.06310786229099424,0.05679544344150319,0.050974971492821944,0.04590612703146663,0.04188411104770633,0.03918312341097095,0.03795403621838803,0.03812865707672313,0.03941832500928206,0.04141645186743421,0.043717188654179055,0.04598197808438234,0.047954918666391996,0.049453725910734644,0.05035507060621059,0.050581704211515456,0.05009292477882185,0.048877966346434765,0.04695152620618586,0.044350755141149195,0.041133232460282707,0.03737563653709686,0.033173021979481764,0.028638922672091914,0.023907173458015185,0.019138162707793394,0.014537853699660855,0.010416377343770683,0.0073534717498653845,0.006292531284638595,0.0072814690728063534,0.00899457429562775,0.010538007745877275,0.011587523911124279,0.012035698219181547,0.011852805137183826,0.01106161520382555,0.009789085331582263,0.008435043844551359,0.007970270434727098,0.00957947236441546],[0.11835259510343855,0.1126976796748466,0.10672761809904008,0.10045458871584942,0.09389844749172122,0.08708874051965751,0.08006743046076496,0.07289273940932468,0.06564478421730625,0.05843411661768658,0.05141484829773107,0.04480421146923519,0.038907646791657965,0.03413473929655698,0.030954702278430522,0.029714492148482992,0.030379718957894035,0.03249216662492722,0.035423059092376585,0.03861865930933375,0.04167727344462808,0.04432964336662024,0.046401297160342934,0.0477831845577247,0.048412748638347575,0.04826237085439056,0.047332362360984995,0.04564665450057087,0.043250080974026425,0.040206599617502684,0.036598079275729084,0.032523481225753326,0.02809850656277908,0.023456266544932287,0.018750847261659476,0.014169875151203529,0.00997782123221615,0.00666679470410732,0.00523080925195833,0.006066548169173196,0.0077496263791834745,0.009274091833597115,0.01032623982288632,0.010812108491786569,0.01069019007778857,0.0099415274476621,0.008619663222576849,0.00703042852000561,0.006205623717099531,0.00775559524394507],[0.11728334771869588,0.11147844922360137,0.10533546214206128,0.09886215079006792,0.09207276654822333,0.08498963446803116,0.07764528480811532,0.07008548755724449,0.06237387750552791,0.05459954436004147,0.046890423944294365,0.039438365474710156,0.032547003288767765,0.02671438635436538,0.022706278357253022,0.021338468527866018,0.022716890491765375,0.025971213774425746,0.03004807421117256,0.034223686356197526,0.03807702481746728,0.04136618576196078,0.04394973307835073,0.04574647851880284,0.04671535285936001,0.04684501090149352,0.04614822574350506,0.04465873294506,0.0424293740146217,0.03953094073036889,0.036051396096517446,0.032095316673366944,0.02778358031789849,0.02325367643995715,0.0186619689388458,0.014192248548832142,0.010085600313280757,0.0067440425073242724,0.0049602572559063795,0.005292074239059357,0.006632955707062078,0.007939551490109251,0.008877534607749541,0.009353630737347012,0.009310152939188476,0.00868698977915742,0.007475424193785687,0.005905275192229569,0.005031588439195971,0.00671183098492236],[0.11657043848881896,0.11066405517417298,0.10440347340031388,0.09779310067954607,0.09084279747398133,0.08356901171569273,0.07599620350075009,0.06815874565549702,0.0601036870608703,0.051895245538901326,0.04362314022025233,0.03542041847117773,0.0275076328816521,0.020317864445259716,0.014851753038980184,0.013054716811309076,0.015662086121151535,0.020525008042214788,0.025878166889638975,0.03097860602442911,0.03550596763081214,0.039299356211709026,0.04227039266168936,0.04437191402487404,0.04558521114378971,0.0459142402554408,0.04538278637443305,0.044033009452296705,0.04192469012611809,0.03913484396075787,0.03575753137610097,0.03190378802409385,0.027701719009896708,0.023297055521405277,0.018855149456690562,0.014567319347145863,0.010670068402249903,0.007497933782024396,0.005556461400247382,0.005200118069957212,0.005854192217104838,0.006702268003358634,0.00739740152095898,0.007834053237306628,0.007928465430609299,0.007576993612582246,0.006734187275667918,0.005621996147198498,0.00521706146672146,0.006974477308331948],[0.11623305601599467,0.11027844918712824,0.10396185953692035,0.0972860041197329,0.09025849536691481,0.08289270791080372,0.07520876328356477,0.06723467532377313,0.05900775010473119,0.0505764658860288,0.042003433853538254,0.033371266088534614,0.024798027060395342,0.01649434492598119,0.009096226910202027,0.006132008844341721,0.010931963395627412,0.01744011751107685,0.02371547019880835,0.029377423984510976,0.03427837361562193,0.03833748052721813,0.041506956940942356,0.04376217700416295,0.04509800681595007,0.045527240701443226,0.045079917125415855,0.04380307429004012,0.04176075880497698,0.039034193773016534,0.035722054609612704,0.0319408347494408,0.02782534077439497,0.023529486865257847,0.019227862504080366,0.015119192036638486,0.011433620314651716,0.008442411028140816,0.006434215063614657,0.005530459077172545,0.0054327912823900724,0.005684246593232968,0.006056927375159563,0.006472421924969151,0.006810334299589292,0.0069024382717128826,0.0066671364034580445,0.006306849037409241,0.006530378194242676,0.008236517699493021],[0.11628006861035554,0.11033278284047605,0.10402480628246072,0.09735915707172903,0.09034385211216275,0.08299282499998965,0.07532699584848125,0.06737556536850883,0.059177689605350026,0.0507849042884807,0.042265261372808206,0.03371203142843927,0.02526701674527965,0.01720328460198652,0.010334212888807443,0.00784522185305813,0.011961498415007026,0.018087258927220375,0.024180668887276154,0.02974108386682065,0.03457887351056506,0.038596057366876164,0.04173672565532617,0.04397197078909465,0.04529425449471669,0.04571501673722886,0.045263628617599534,0.04398700395986378,0.041949584662157945,0.03923356325389796,0.03593926677152707,0.03218565491472855,0.028110903777648206,0.023873056906764504,0.019650686419677127,0.01564318200686367,0.01206860416614789,0.009150112645214696,0.007063353149626608,0.005818230727749677,0.005198234529667491,0.004967262551336774,0.005087895779696565,0.00557455847001028,0.006249739162111238,0.006841693248775651,0.007206960714597885,0.007473570485700221,0.008112797947564513,0.009749590507182696],[0.11670932564003737,0.11082442230998221,0.1045890561578576,0.09800848087384882,0.0910936811088687,0.08386263625397235,0.07634195338414175,0.06856911551251796,0.060595848354898736,0.052493703222817746,0.04436442664483111,0.036361608090116876,0.028741084302197187,0.021986295218835484,0.017077691459489473,0.015531300980455237,0.017750744850972385,0.022124272039815637,0.027127971849029854,0.03199616342682833,0.03636643725215412,0.04005092175802992,0.0429454095887991,0.04499332914035118,0.04617027496222536,0.04647681922441533,0.04593499128764267,0.04458654474357258,0.04249217561758691,0.03973128284842637,0.03640204541419941,0.03262166753238117,0.028526664967576085,0.02427303795666588,0.020036047602706067,0.016008856319971627,0.012397680283964707,0.009405854733460357,0.007187648104233075,0.0057585359002274425,0.0049562127247053025,0.004618938794267171,0.004776564736017735,0.005453489998787314,0.006408248763584275,0.0073211970291124345,0.008028146305698224,0.008610794584367133,0.009424503605479948,0.010982400454642258],[0.11750778705215086,0.11173712989615128,0.10563416896272422,0.09920790644590098,0.0924742025322246,0.08545751264822607,0.07819324413378695,0.07073112917785108,0.06314035249489476,0.05551784509216469,0.048002463760465304,0.04080007415206757,0.034226922572420465,0.02877108608123871,0.025110640102461435,0.023874980299027425,0.025087876470575143,0.028029785307123804,0.03180108871771939,0.035730115230509576,0.039396848748604905,0.042548186642922675,0.04503166660784697,0.04675765326967708,0.04767910553269537,0.047780709109324145,0.04707292440213918,0.045588683430025354,0.0433815665947257,0.040524825007384205,0.03711087263830543,0.03325099339308097,0.029075058860828944,0.024731071405260582,0.020384369243367353,0.016216395786994468,0.012422989512257107,0.0092111959503611,0.006785716823219487,0.0052884557531144944,0.004671294123519993,0.004711465106543754,0.0052372467202136085,0.006122037868699601,0.0071509708131607536,0.008089816662775915,0.008818214156088968,0.009414592434690722,0.010195733216742338,0.011638978086997077],[0.11865246119565155,0.1130423802835269,0.10712441044772174,0.10091215480548943,0.09442726158807599,0.08770155225623326,0.08077989566038883,0.07372422244486765,0.06661930780626393,0.05958127183365436,0.05277000773829186,0.04640619868948097,0.040789603771795295,0.036301649329081115,0.03334859860707485,0.03220008482278216,0.03279576122825896,0.0347297811240037,0.037448152558288574,0.040445296484846675,0.04333852242596752,0.04586176819136881,0.047837683106019234,0.049152815190034845,0.049740421598130385,0.04956948912354272,0.048637901395988406,0.04696820982579936,0.04460500556225453,0.041613254238408524,0.038077170367530305,0.03409932810032436,0.029799779184802828,0.025315037416440946,0.020797013681006105,0.016412673862115652,0.012347286919177297,0.008820071241223325,0.006130709938697636,0.004689305403031583,0.004620758351634657,0.005337705428754651,0.0062982063311652755,0.007294698092984393,0.008207335745412195,0.008922891515195243,0.00939549804452215,0.0097382132642783,0.010290454816609116,0.01156007103035543],[0.1201120081207192,0.11470158309486211,0.10901189220961935,0.10306126929949604,0.096877031653767,0.09049776958545222,0.08397632300688333,0.07738369013407338,0.07081414542726792,0.06439173658929503,0.05827777709532616,0.052677250308729495,0.047838058906065434,0.0440306038143418,0.04149232563115426,0.04033980216274907,0.04049535842819425,0.041692556085751786,0.04356188367988223,0.04572947517600141,0.047876219728458305,0.04975509680384209,0.05118632726949362,0.05204590780677841,0.0522545848196009,0.05176926228206468,0.05057684184218218,0.04868995708815115,0.04614404118524971,0.042995271145245914,0.03931903893396793,0.03520868800774315,0.030774347010534376,0.02614186050042037,0.021452246049282683,0.01686335293440952,0.012559320127598217,0.008786505796766824,0.005967707219463831,0.004807957323233697,0.005377351968991667,0.006602513965853307,0.007796228890818387,0.008756959025854376,0.009416356489941791,0.009733581240884751,0.00972616446933776,0.009562785998355233,0.009668598160016839,0.01068132760552412],[0.1218487802406164,0.11666885546655106,0.11124039188166286,0.1055859584653926,0.09973760277327678,0.09373903574420789,0.08764829946019094,0.08154096172167827,0.07551375392929408,0.06968823296481859,0.06421330102416684,0.05926402011326241,0.055032186717081884,0.05170296368133084,0.04941524066325311,0.04821499230536193,0.04802504258836325,0.048653013478396914,0.04983488159566307,0.05128877217912557,0.0527553945332112,0.05401822639416753,0.05490849924684682,0.05530238899360771,0.055115566156429964,0.05429766996125301,0.05282764719268242,0.05071012073196001,0.0479726550536566,0.04466370879187853,0.04085108032721982,0.03662071954943431,0.03207591696165823,0.027337188450936717,0.02254393180588863,0.017860956829902703,0.013498710073103484,0.009770709097200505,0.0072123223513531984,0.006459857490293381,0.007251995764693218,0.00854671011962753,0.009700183850223382,0.010474142906714203,0.01078160420632442,0.010591440229262138,0.00994087578845672,0.009031462734359225,0.008415567248980776,0.009043668259446289],[0.12382104180024961,0.11889395657866576,0.11374926197446567,0.10841283443372383,0.10292002458328897,0.09731752484000258,0.09166545825263216,0.08603956712870811,0.08053319053139522,0.0752583706009422,0.07034486471886668,0.0659351216237299,0.06217280489370329,0.05918321313475995,0.057047234156333726,0.05577608376764512,0.05529810643387206,0.055465699600502585,0.05608015028579563,0.05692334354990724,0.05778499053664069,0.05848001116895563,0.05885655549767272,0.058797709794130584,0.058219904708083026,0.05707006828071284,0.05532262823484066,0.05297684933161694,0.05005466017580785,0.046598982207390935,0.042672551441156906,0.03835729814158171,0.03375455547378492,0.02898683012380983,0.024202892328075605,0.01959016208641366,0.015402236724592854,0.012007383193698531,0.009896019028675804,0.009372685304978506,0.010039966373636718,0.011112464228384975,0.012028623338926105,0.012506646188436835,0.012413564136756513,0.011690059476769807,0.0103465758475843,0.008545023698765938,0.006887585101820812,0.006902620279782382],[0.125985130720521,0.12132505002864377,0.11647695615973605,0.11146889030050326,0.10633791786211895,0.1011315610950374,0.09590921113326822,0.09074330631603547,0.08571988937006378,0.08093790315256423,0.07650628438793476,0.0725377056049821,0.06913801267903465,0.06639145619896962,0.06434392574566351,0.06298883967102009,0.06226123178213843,0.062043253182265126,0.06217959319185307,0.06249746195672411,0.06282526699563712,0.06300642043862928,0.06290755412991496,0.062422197506227434,0.06147149664924416,0.0600033428649291,0.05799084813179123,0.05543072188902372,0.05234184944251146,0.048764244048830556,0.044758524948781374,0.040406162547899374,0.03581096436835102,0.031102728259197795,0.026444729969858492,0.02204736072505923,0.01818764718571152,0.015214873708660752,0.013463663961078075,0.012996638888057965,0.01343135047189173,0.014182846582352478,0.014776824612841175,0.014919195282129743,0.014443456835607153,0.013261667212557969,0.01135221036607682,0.00880812305469421,0.006104589372076159,0.005225526326744479],[0.12829738414250244,0.12391106425829998,0.11936388913283606,0.1146848942271304,0.10991135874388987,0.10508977697520962,0.10027662987411076,0.09553872034286831,0.09095271165841798,0.0866033688467111,0.08257990211075054,0.07896986419149729,0.07585042819603025,0.07327770174923162,0.07127591237177507,0.06982929385951635,0.06887949537542674,0.06832987738610131,0.0680557275936873,0.06791756833134999,0.06777432411651664,0.06749405447952851,0.06696136548171988,0.06608171882722559,0.06478339323492487,0.06301793643886514,0.060759804454753215,0.05800569093613693,0.05477389274609579,0.05110397083466523,0.047056956913596355,0.04271643073071349,0.038190948790881286,0.0336184861826172,0.0291734346368626,0.025074988949726686,0.021588615763417297,0.018994141196674197,0.017479916054681244,0.01698971277266361,0.017188739730976024,0.017623588628506687,0.01789726902564999,0.01773077885453569,0.016950441091320823,0.015464142613240504,0.01325808178392955,0.010446044115036017,0.007510956201387788,0.006216355342514625],[0.13071572039189203,0.1266035360778866,0.12235452871812644,0.11799766172256124,0.11356916206249552,0.10911306948529549,0.10468147913027635,0.1003342623468986,0.09613797972557629,0.09216364787743435,0.08848303381350421,0.08516329679388894,0.08226014448529977,0.07981022220902116,0.07782407023556319,0.07628135572226687,0.07512987322910299,0.07428891841280466,0.0736564105247927,0.0731181684322616,0.07255746313095339,0.07186336324104249,0.07093710790698952,0.06969640734494736,0.06807799016265267,0.06603888203524716,0.06355689901753911,0.06063076545390586,0.05728018696094737,0.05354615773030225,0.04949176961043784,0.0452038070068031,0.04079539870896373,0.036409763079634484,0.03222407689317473,0.028449451043532623,0.02531627356280954,0.02302673179051634,0.021667960041622962,0.02113285217972622,0.021132243983650392,0.021301442930301815,0.021308471358097696,0.020904777190104813,0.01993206287748809,0.018318984304160634,0.016094782946659805,0.013454928786944946,0.010963585305697316,0.009922927318679562],[0.13320083664617796,0.1293579188287185,0.12539875407357437,0.12135134551457964,0.11724989681603899,0.11313501344360335,0.10905355278882993,0.10505795001936437,0.1012048172622272,0.09755261434990048,0.09415825031137025,0.0910726291606641,0.08833541701824058,0.08596964696928833,0.083977086389725,0.08233540537299631,0.08099796751969571,0.07989651882880298,0.07894636611676667,0.07805309692563252,0.07711970135176234,0.07605312306251791,0.07476964290870595,0.07319889765409356,0.07128663528962285,0.06899647268772323,0.06631097645155237,0.06323237939456033,0.05978321278746499,0.056007100992850424,0.051969930922177145,0.047761540296934205,0.04349786334911495,0.03932288314276721,0.03540827874981362,0.031945739102904526,0.029123211914751635,0.027077469604918847,0.025832420042406858,0.025261820454024652,0.025114595512415138,0.025089678412794136,0.02490952223924288,0.024362073943288765,0.02331683517005764,0.021734658650015115,0.01969139920622098,0.017438153082271427,0.015516956972156007,0.0148340453724522],[0.13571703255603726,0.1321344020551923,0.12845259089211078,0.12469795857283844,0.12090200843963902,0.11710132589254359,0.11333716562121411,0.10965456087256838,0.10610082531822132,0.10272334482870268,0.09956662900338449,0.09666872245151596,0.09405725838679908,0.09174563668022209,0.08972995612816784,0.08798734337364791,0.08647614577575098,0.08513811519997044,0.0839023106446779,0.08269013212121464,0.08142076832808731,0.08001640956062135,0.07840677921100184,0.07653277784583412,0.07434923909186517,0.07182693302866554,0.06895402164102764,0.0657371903583169,0.06220266885820796,0.058397321469659126,0.05438991984662042,0.050272557683878026,0.04616181250018282,0.04219849017399475,0.03854335059257178,0.03536424379223055,0.032809346943372356,0.030966238512883448,0.029820650419923326,0.029241570193742007,0.02900898711195303,0.028869827643181,0.02859202140541842,0.027999904567773813,0.026993767830984425,0.02556534534552705,0.023821570871828603,0.02202492690981442,0.020638916395339307,0.02029960201008541],[0.13823270231556492,0.13489832383957534,0.13147846289947437,0.1279973515499889,0.12448337469346187,0.12096882538208821,0.1174893367016422,0.11408290452005057,0.11078842749562444,0.10764372646835389,0.10468307208380624,0.10193434850647881,0.09941610132574462,0.09713483157174736,0.0950829637361711,0.09323789269625173,0.09156238374309314,0.09000638318058322,0.08851005495900877,0.08700766645475284,0.08543185790223554,0.08371785591509813,0.08180730214323266,0.07965151454652288,0.07721413705508692,0.07447323771397829,0.07142297852629433,0.06807500592525863,0.06445970417040371,0.0606274114410051,0.056649596983584044,0.052619780903246226,0.04865354339079303,0.04488618799844464,0.04146549037015081,0.038536064549356465,0.036213078245000155,0.0345489870118027,0.033506707529770696,0.03295671431374556,0.03270410584178986,0.032532930123560413,0.03224852972464826,0.03170774471681864,0.030838476863324246,0.029655492586939235,0.02827857965746712,0.026952948692920694,0.026055573914007507,0.02604414637522392],[0.14072055323364044,0.13762026723665902,0.13444509549479194,0.13121683478080393,0.12796054305266452,0.12470417948895712,0.12147796244847904,0.11831339256237329,0.11524190647452127,0.11229316221997199,0.10949301202540715,0.1068612894664077,0.10440961463589059,0.10213948405377486,0.10004093754568257,0.09809206225340746,0.09625949913270593,0.09449997630514265,0.0927627419008891,0.09099264769337377,0.08913357384996597,0.08713189234992734,0.08493972818637993,0.08251786741547346,0.07983825324898502,0.07688608713644289,0.07366160184810097,0.07018159456251205,0.06648079624623922,0.0626130976055681,0.05865252309933475,0.0546935892944758,0.05085022777114029,0.04725175637097446,0.044033628884107515,0.04132065199143709,0.03920256665604778,0.03770743030216445,0.036784472798815776,0.036307856634630105,0.03610248485270089,0.03598098642001262,0.0357784778200584,0.03537837223500774,0.03472997544891293,0.033861680658939484,0.032892117146832336,0.03203623957789164,0.031594141874023145,0.03190283208065473],[0.14315761211873393,0.14027592730900101,0.13732718762711915,0.13433059150491308,0.13130782041682168,0.12828261645065633,0.12528012355570897,0.12232596400282905,0.11944504109552173,0.11666009026158294,0.11399004292042149,0.11144831689202275,0.10904119494534094,0.1067664868030511,0.10461267599918016,0.102558721986274,0.1005746197062877,0.09862272523243523,0.09665975821239381,0.0946393131280585,0.09251466904987789,0.09024168702783918,0.0877816189480841,0.08510370739571123,0.08218751692411075,0.07902499000732208,0.0756222567821736,0.07200123970019219,0.06820107374866002,0.0642792935475432,0.06031258981971344,0.05639666264201267,0.052644252735941394,0.04917984945437528,0.04612915594201979,0.04360194559773293,0.04166961551464691,0.040343591617399095,0.03956458519503276,0.039210333580061554,0.03912043096847421,0.03912863012017659,0.03909241485851762,0.038914976871294714,0.03855991955842924,0.03806079683273675,0.03752613404609909,0.03713695490313335,0.03712966570683909,0.03775677465095472],[0.14552507639864284,0.14284582263120923,0.1401049429208714,0.13731898698272102,0.13450632397811685,0.13168669626382148,0.12888058127809668,0.1261083500072591,0.12338922858023078,0.12074009499430077,0.11817417434806878,0.11569972942113138,0.11331887266219173,0.11102664267128275,0.10881048557128546,0.10665025501968127,0.10451879556096504,0.10238311069025181,0.10020605231788456,0.09794841608283818,0.0955712973624425,0.0930385595266498,0.09031928578413226,0.08739012082366304,0.08423744846701788,0.0808593873224856,0.0772676097780636,0.07348899233902677,0.06956707575901434,0.06556323219149426,0.061557272112140855,0.057646935157306595,0.053945274791474894,0.050574455522527643,0.04765431020109493,0.04528496026682894,0.04352572917621929,0.04237689682315647,0.04177316682289351,0.04159413302058979,0.0416887748729378,0.041904920876278735,0.042115188492042176,0.04223563173989494,0.04223733222581385,0.04215232228373749,0.042074071048090016,0.042150619596343135,0.04256694278395781,0.04351459291585751],[0.14780805866410282,0.1453149100401806,0.1427635269476177,0.1401678435395373,0.13754305739238337,0.1349051860258135,0.13227047169553002,0.12965463400587107,0.12707198549750287,0.1245344453561956,0.12205050909744751,0.11962425437611278,0.11725448053397365,0.11493408720293503,0.11264979112420993,0.11038225861533861,0.10810669568233441,0.10579389421360523,0.10341168909525551,0.10092674581564148,0.09830657739946165,0.0955216857776684,0.09254773435349188,0.08936768083393958,0.08597382596490617,0.08236975773105518,0.07857218458818462,0.07461264646060316,0.07053905508294678,0.06641692360847697,0.06232996519199281,0.05837943162276849,0.05468111712333435,0.05135849571951639,0.04853043750019472,0.046293204940363014,0.04469965229370593,0.043742700988756274,0.04335155806780002,0.04340453342952581,0.04375413591785806,0.044255216365397455,0.044788450354884775,0.04527615824199722,0.04569094707302646,0.04605851853077612,0.046455113076367634,0.046998813154686625,0.047833519526410864,0.04910587152296003],[0.14999526389408593,0.14767214692198488,0.14529249722258852,0.14286772554603974,0.1404100464659017,0.13793205472798453,0.13544618441460293,0.13296405730957567,0.13049573971297446,0.12804894223159297,0.1256282132262986,0.12323419124080841,0.12086299187929879,0.11850580723836182,0.1161487889480815,0.1137732686307875,0.11135634385519227,0.10887182729539552,0.10629152698493732,0.1035868015084632,0.10073031960251722,0.09769795060494235,0.094470719694799,0.09103677703696982,0.08739334853879947,0.08354865274439084,0.07952377697595057,0.07535449690955896,0.07109298209281371,0.06680922956806389,0.06259186842689045,0.05854763185897004,0.05479828823636457,0.051473309574398184,0.04869656619122861,0.046566863598525854,0.045135897381363387,0.04439173121258056,0.044256781678194496,0.04460333543098468,0.04528062174055752,0.04614315399478019,0.04707276554063843,0.04799205639150159,0.048870355709926594,0.04972395830370317,0.05061160480007462,0.05162530152283812,0.05287645002928105,0.054478229493657715],[0.15207862957226423,0.14991003289968793,0.14768523671429443,0.14541326000486007,0.14310354967805824,0.14076558665259095,0.13840840350678266,0.13604002391447634,0.1336668443966702,0.13129299037643047,0.12891968987336958,0.12654471766223793,0.12416196836608581,0.12176121695443831,0.11932811835737925,0.11684448442802096,0.11428885771817676,0.11163738015871033,0.10886493417180712,0.10594651735926142,0.10285880225866872,0.09958183092864888,0.09610079998320582,0.09240790345339274,0.08850421572914757,0.08440161097122759,0.08012472317491773,0.07571294318031176,0.07122240830578727,0.06672783568340188,0.06232382928380821,0.05812488245875899,0.05426266174695647,0.05087844429632217,0.048108448566806336,0.04606159008332778,0.04479397468884542,0.04429025369682389,0.04446271703129483,0.04517074755301165,0.04625202177227333,0.0475528238324867,0.0489495200758557,0.05035989016006041,0.05174653038927669,0.05311484989115006,0.054507184701146794,0.05599367899610026,0.057660388096945125,0.05959557000733969],[0.15405295102643585,0.1520241528615999,0.14993841006787273,0.14780250613856655,0.14562334760065665,0.1434076046689902,0.14116128675310985,0.1388892648878919,0.1365947612289049,0.13427883423792702,0.1319398960768374,0.12957330478320284,0.12717107672456698,0.12472176355816414,0.12221053193680854,0.11961947376865373,0.11692816110942165,0.11411444464609477,0.11115548054077022,0.10802895941118162,0.10471450519519696,0.10119521153227568,0.0974592891341099,0.09350180860486465,0.0893265377458118,0.08494788803680009,0.0803929973732132,0.07570397661729551,0.07094031793072088,0.06618136568969157,0.06152851465913434,0.057106310309428344,0.05306076469232323,0.04955205395369961,0.046738138271172194,0.04474779505046746,0.04364819581280511,0.043420996822605605,0.043962174949676074,0.045108147673582025,0.046674649674539104,0.04849122809183718,0.05042273402656693,0.05237830794675818,0.05431194378013734,0.056218223263316255,0.05812523925309992,0.060085608150329,0.06216610846421316,0.06443668403252278],[0.15591550788709055,0.15401273574064792,0.15205145361932382,0.1500363795443327,0.14797210902447566,0.1458627916138671,0.14371176081848003,0.14152112995505217,0.1392913728014189,0.13702091409704703,0.13470576039176083,0.13233920552862297,0.12991164635105568,0.12741054243553146,0.12482054857046915,0.12212384067318993,0.11930064577518311,0.11632997599584627,0.1131905567013564,0.10986193191622734,0.10632572684431034,0.10256704894225488,0.09857601577563119,0.09434940988057873,0.08989247772862874,0.08522091083083022,0.08036306982203952,0.07536253085114608,0.07028103115382175,0.06520182603350273,0.06023324935303531,0.05551170999821704,0.05120217912776681,0.04749227844910965,0.04457421595518781,0.0426103578971157,0.04168806615239323,0.041785107514631006,0.04277032328145028,0.044442118297727505,0.0465810488243891,0.04899108107854679,0.051520772784786305,0.054068704910955424,0.05658029919751385,0.059040896275302755,0.06146738382529656,0.06389920248342307,0.0663890772861703,0.06899388526791267],[0.15766570254324838,0.15587623797550587,0.1540261048163099,0.15211813175126723,0.15015482851063647,0.14813809744853745,0.1460689128893389,0.14394698057044258,0.1417703942764417,0.1395353112815991,0.1372356719284258,0.1348629909699133,0.13240624866376768,0.12985190769474153,0.12718407778761304,0.12438484370650525,0.12143476494268325,0.11831354780345647,0.11500088402772372,0.11147744567531952,0.1077260249500955,0.10373281072422508,0.09948880160961521,0.09499136927459385,0.09024600636448873,0.08526832221872452,0.0800863878715625,0.07474357879584662,0.0693021102933726,0.06384747122613028,0.05849383273468064,0.05338997598802055,0.04872379656828416,0.04472024519245324,0.041622941902515184,0.039648772624865776,0.038919481474898224,0.039405825984477116,0.04093032611819606,0.043230360900814606,0.04603476053380215,0.049113866589740526,0.05229777674273078,0.05547536524174171,0.058585741694783436,0.06160806976907373,0.06455174899803831,0.06744730037892276,0.0703378910752842,0.07327153565914309],[0.15930471770422203,0.1576169567394897,0.15586597314874598,0.1540528833695064,0.15217832890805008,0.15024222075209348,0.14824346260618437,0.1461796645378032,0.14404686223252736,0.14183926031818453,0.1395490207164828,0.1371661183073922,0.13467828601741538,0.13207106959779158,0.12932800889905893,0.12643095769407778,0.12336054862934913,0.12009680447706823,0.11661989242512248,0.11291101562678907,0.10895343657433858,0.10473363101379135,0.10024258018332738,0.09547722466327459,0.09044212747211372,0.085151431117557,0.07963124912499775,0.0739227152317688,0.06808602997815713,0.062205986159171056,0.05639954654995295,0.05082579839314604,0.045697149083158486,0.041285986890290345,0.03791103061920262,0.03587787587847468,0.03536735572798179,0.0363354063979492,0.03852276189086652,0.04157027491748081,0.04513615299070166,0.04895276420700705,0.052834372764810573,0.05666474518713572,0.06038131364591866,0.06396136609244575,0.06741089780467453,0.07075547875510275,0.07403249053859041,0.07728439743349459],[0.16083519743423424,0.1592386754228063,0.15757615255391125,0.15584720772365743,0.1540508223138816,0.152185154601545,0.1502473013395494,0.1482330571162287,0.1461366848148341,0.14395071282617755,0.14166577631802088,0.13927052055763078,0.1367515838177568,0.13409367569614958,0.13127976383642284,0.12829137833110119,0.1251090389708862,0.1217128065761944,0.11808295660398287,0.114200771820545,0.1100494518851912,0.10561514215228938,0.10088809315691709,0.09586397811901679,0.09054542183965747,0.08494383670505948,0.07908173106485064,0.07299577100178091,0.06674106971049326,0.06039749318316943,0.054079235707031346,0.04794939633002751,0.04224086929658223,0.03728004274879158,0.03349183529313581,0.03132965528677124,0.031081380848894873,0.03266873552463957,0.035681505959688053,0.039610863737687574,0.04402866792351238,0.04863448587990863,0.05323688714173224,0.057723390103156226,0.06203635426615505,0.0661561251721867,0.07008924413912712,0.07385971853049025,0.07750210673379261,0.08105578993529777],[0.16226095409124391,0.16074634216397501,0.15916287405717627,0.1575087614070595,0.15578152348913316,0.15397778859215588,0.15209308878223976,0.1501216575937715,0.1480562422097542,0.14588794334406935,0.14360609709727518,0.14119821334032193,0.1386499845662012,0.1359453776153093,0.13306681832536246,0.12999547621093469,0.1267116530932889,0.1231952766302559,0.11942649746414878,0.11538638779862043,0.1110577403016942,0.10642597015864522,0.10148013111034017,0.09621407049848381,0.09062777249216494,0.0847289799701645,0.07853525789984989,0.07207679194871847,0.06540046030354728,0.05857618315655646,0.051707448419651504,0.04494954447848037,0.03854140219042629,0.03285685371737397,0.028459941868621125,0.026057756185776486,0.02614992423413445,0.028571681102215075,0.032619994115435,0.037567331370689766,0.042903343166212894,0.04831819141443419,0.05363392600491606,0.058753888478432784,0.06363255621135601,0.06825782291785223,0.07263990587281781,0.07680369399937781,0.08078294067211438,0.08461556275966686],[0.16358670227371733,0.16214578117933542,0.16063319681676133,0.1590459582291357,0.15738031055289642,0.15563156042638351,0.15379389937056331,0.15186023361487216,0.1498220303442738,0.1476691914973423,0.1453899668959288,0.14297091851037297,0.1403969469893784,0.13765139021414877,0.1347162016637158,0.13157221398489904,0.1281994906106292,0.12457776589463429,0.12068697240698112,0.11650785318373641,0.1120226573300645,0.10721592006962109,0.10207533407477334,0.09659272937764964,0.09076519752763426,0.08459642824915682,0.0780983867229727,0.07129357476505338,0.06421835221228082,0.05692829214206524,0.04950766222732997,0.042087755320530267,0.03488504322129609,0.02828319540519404,0.022989948787508686,0.020150837396807463,0.02073907398170992,0.024342522867218823,0.029670366224713397,0.03573323504646434,0.041996797442918954,0.048188724762871685,0.05416905921321011,0.059868376725825935,0.06525853495593444,0.07033759772766102,0.07512102066745698,0.07963572788855457,0.08391562420063163,0.08799792918096787],[0.16481781999360465,0.16344343602870276,0.16199473552579746,0.16046768332089806,0.15885742866388522,0.15715815201449332,0.1553629131680614,0.15346350818835433,0.15145034373588803,0.14931233817829653,0.14703685924473875,0.14460970785603935,0.14201515708578064,0.1392360540001027,0.1362539904632703,0.13304954702149008,0.129602611881186,0.12589277501046775,0.12189979576732045,0.11760414146286538,0.11298759419396938,0.10803392448451028,0.10272963329176905,0.09706476970521756,0.09103384203472613,0.08463685878728956,0.07788057158699688,0.07078006334383827,0.06336097761043454,0.05566303735202087,0.04774638646971967,0.039704741118162246,0.03169694658283479,0.024034858524804394,0.017456227806711272,0.013785998794746275,0.015225774746477903,0.02053886996829033,0.027322606952009085,0.03447495240541924,0.04157496116076118,0.0484413223815664,0.05498884650816574,0.06117956040268477,0.06700307321827649,0.0724670657866828,0.07759167678354384,0.0824055334946239,0.08694255981298728,0.09123923623975835],[0.1659601367177834,0.16464614362540372,0.1632554221225002,0.1617830445571593,0.1602232332308137,0.15856922630976064,0.15681314753741996,0.15494588633352216,0.15295699568957974,0.1508346158204183,0.1485654317314861,0.1461346726562261,0.14352616068563456,0.14072241487314568,0.13770481571624463,0.13445383329709087,0.13094932064585232,0.12717087222976087,0.123098246030081,0.11871184660228921,0.11399326596277318,0.10892587924534933,0.10349549299057006,0.09769104595056999,0.09150536598491374,0.0849359932556888,0.07798609241553876,0.07066550179888291,0.06299202350589811,0.05499319352834235,0.04670913497211131,0.03819821286473673,0.029551267502297345,0.020938936285905638,0.012837853502634606,0.0075784264329622295,0.01072329602582825,0.018146712998175135,0.026199530188155545,0.03418223067601053,0.04189589816623757,0.049257198952541756,0.056226941688574845,0.06279004361741622,0.06894764161904073,0.0747128434365119,0.08010774523220254,0.08516094355175689,0.08990528319200523,0.09437577622913433],[0.16701974755135165,0.1657609376370599,0.16442329985577417,0.16300115884681027,0.16148796989872435,0.15987620210833317,0.15815722719441694,0.1563212197852429,0.1543570756172174,0.1522523544688693,0.14999325475585423,0.14756462649402055,0.14495002879057142,0.14213183717084577,0.13909140494514902,0.13580928155016034,0.13226548946807676,0.12843986005051655,0.12431242746998675,0.1198638791961448,0.11507606093868732,0.10993253399329424,0.10441918345880802,0.09852487700472495,0.09224217606110775,0.08556810518190408,0.07850499257450168,0.07106140951646246,0.0632532692874561,0.055105227347779236,0.046652747686739264,0.03794590477652212,0.029058667266282544,0.020120738027777734,0.01149156758735133,0.0056255439453016184,0.010134931751340828,0.018364136477520835,0.02685503922951919,0.035162870915405486,0.04315631241445666,0.050774680907583726,0.05798725562052474,0.06478172101420093,0.07115922850820769,0.07713140131873865,0.08271800529346264,0.0879448825203417,0.09284202386233688,0.0974417625975987],[0.16800285259816286,0.16679487984988187,0.16550634787354926,0.16413097117225686,0.16266158909584993,0.16109006476543355,0.15940719109799226,0.15760260911413046,0.15566474419136592,0.1535807662148549,0.15133657964095085,0.14891684930735105,0.14630506739918098,0.14348366634038148,0.14043418157677218,0.13713746732725257,0.13357396749848766,0.12972404319697478,0.12556835775411956,0.12108832004432293,0.11626658729434022,0.11108762979743153,0.10553836236115507,0.09960885168345854,0.09329311667075858,0.08659005315144827,0.07950454250125996,0.07204886172960362,0.0642446413471417,0.05612592712189909,0.047744722174195946,0.03918282980856702,0.030582251716855087,0.022241156096252074,0.014987896916772651,0.011446566276263654,0.014599777402921347,0.02152543637692067,0.02945951293538766,0.037532368524341386,0.04544483261924706,0.053066027627568936,0.060330861161672085,0.06720755327617493,0.07368471507101988,0.07976495393058569,0.08546098853466409,0.09079285339422996,0.09578564520693245,0.1004675954542942],[0.16891562037244617,0.1677549180303877,0.16651233459783044,0.1651811044919892,0.16375359327966793,0.16222121122214034,0.1605743351111161,0.15880224307086174,0.15689306739453873,0.15483377072622506,0.15261015097253233,0.15020688022280176,0.1476075826869524,0.14479495625917346,0.14175094184095305,0.13845694408947096,0.13489410690328268,0.1310436468515975,0.12688724807143092,0.1224075231389974,0.11758854642736002,0.11241647007789307,0.106880238967876,0.10097243186241865,0.09469027501168191,0.08803690932291633,0.0810230588331862,0.07366938191024296,0.06601007034785335,0.058098901724752586,0.050020494206362176,0.041913493036716626,0.034023171365786455,0.026828318392223518,0.021317484509596533,0.01916853983061234,0.021405796328812256,0.02682381397601863,0.03373706853604237,0.041190440040570195,0.0487299327717161,0.056129959517494984,0.06327081621861551,0.07008769725986595,0.07654782684266948,0.08263897098720015,0.08836289818545223,0.09373116877197424,0.0987621187744335,0.1034785245311215],[0.16976407401357507,0.16864776878133947,0.16744869819890656,0.16615973874393583,0.16477291519558157,0.1632793279233617,0.16166908950994544,0.15993127499296023,0.15805389035768175,0.1560238641483369,0.15382706718141628,0.15144836534452766,0.1488717103711153,0.14608027333769952,0.1430566255028736,0.1397829710906855,0.13624143684448986,0.13241442381791482,0.12828502817771262,0.12383754014183658,0.11905803415329419,0.11393506997490224,0.10846053528577866,0.10263067864643646,0.09644741312732144,0.08992002654935945,0.08306753619026015,0.0759221190531371,0.06853442800754457,0.060982370127773126,0.05338649020052857,0.045938190782256146,0.03895193433694344,0.03295249431313207,0.0287582613460494,0.027320664964852744,0.02904417418516555,0.03334225456817187,0.03922232295521269,0.045899490929558265,0.052887584592189625,0.059902155947122844,0.0667760918545368,0.0734106827137302,0.07974909435291522,0.0857615947649328,0.09143679756975147,0.09677606243016841,0.10178963123907811,0.1064937817446752],[0.17055399895153153,0.16947982383608867,0.16832245247298397,0.16707451720564523,0.1657278254763766,0.1642733001746146,0.16270093027928353,0.16099973579247687,0.15915775129145723,0.1571620326808689,0.15499869190775623,0.1526529645226415,0.1501093150617788,0.1473515853409179,0.1443631909673198,0.14112737180487153,0.13762750292174952,0.133847473930669,0.12977214691891792,0.12538790684565257,0.12068332412547185,0.11564995837648094,0.11028334710472634,0.10458424707869501,0.09856023574626697,0.09222784673156545,0.08561552779426057,0.07876790812498392,0.0717522059900221,0.06466818520348812,0.057663929788319385,0.050960489713132454,0.04488686229685563,0.03991428443672651,0.03663830788538497,0.03560716239236345,0.03700401660285618,0.04050147665720907,0.045490953385392434,0.05138585928200734,0.05774683750265986,0.06427683390835488,0.0707822167749413,0.07713876587827159,0.08326850816032541,0.08912486151226609,0.09468304862475031,0.09993369381564393,0.10487834672213915,0.10952620742470125],[0.1712908705718471,0.17025707816213764,0.16914011636651516,0.16793247839626685,0.1666258677958682,0.16521115128061384,0.16367832277775407,0.16201648246281725,0.16021383491475125,0.1582577108028089,0.15613461677327403,0.15383031844687614,0.15132996170654875,0.14861823780967373,0.14567959838571432,0.14249852720152226,0.13905987686482582,0.13534928063698803,0.1313536525972882,0.1270617940795993,0.12246513141411988,0.11755862084891631,0.11234187316646956,0.10682057626778477,0.10100833416994368,0.09492910370882625,0.08862050780453293,0.08213845109095057,0.0755636672778376,0.0690110467467071,0.06264260357505938,0.056683964994790226,0.05144022904514184,0.047296377283363306,0.04467104303896436,0.0438958654034463,0.04506311378764335,0.04797109144229883,0.05222679232720942,0.057401678077684405,0.06312881395780616,0.06912951963240979,0.07520443553550088,0.08121557576443904,0.08706998332417426,0.09270729559069986,0.09809078474387994,0.10320093622879621,0.10803076950268205,0.11258234324067891],[0.17197980033243296,0.17098507815381805,0.1699076652889967,0.16874001156872562,0.16747381958411123,0.16610000948751358,0.16460869586133237,0.1629891803012872,0.16122996370506018,0.15931878258592194,0.15724267405837342,0.1549880744956155,0.15254095727957992,0.14988701561651643,0.14701189716433444,0.14390149833685453,0.14054232778838577,0.13692195098310886,0.1330295312642121,0.12885648795837376,0.12439729951356915,0.11965049054410413,0.11461985750044758,0.10931601067390458,0.10375834321558836,0.09797758376722276,0.09201914912339405,0.08594757920878272,0.0798523731567283,0.07385544322241071,0.06811988157609998,0.06285819365784084,0.058334692492924244,0.05485128385953584,0.05270288380404702,0.05210068884550651,0.05309508051892156,0.05555270292359359,0.0592074878908181,0.06374508081371828,0.0688694713908056,0.07433452018827053,0.07994973047222417,0.08557407222816911,0.09110655245158616,0.09647727535021201,0.101640076204727,0.10656675012758744,0.1112425894694708,0.11566292080333732],[0.1726254986930077,0.17166888809440115,0.17063050223151788,0.16950283366680224,0.16827767605595814,0.16694610037077107,0.16549844399627292,0.16392431624215434,0.1622126241671599,0.1603516229796027,0.15832899566443878,0.1561319669263155,0.15374745707193385,0.15116228214546648,0.14836340756249236,0.14533826377609374,0.1420751343089098,0.1385636290071265,0.1347952589007806,0.13076413397237865,0.12646781195066972,0.12190833560519969,0.11709350866780405,0.11203847711053831,0.10676770306642548,0.10131744103442136,0.09573884227828874,0.0901018019619286,0.08449957327020909,0.07905389474970034,0.0739197134899075,0.06928727319519086,0.06537730719115399,0.06242329073399579,0.06063630092404809,0.060157173134795516,0.06101517536460287,0.06311746018524773,0.06627662035342388,0.07025892348165189,0.07482862899215584,0.07977547607704129,0.08492582124609879,0.09014341691946874,0.09532536163799196,0.10039657959435105,0.10530441326276552,0.11001390254454618,0.11450385633137858,0.11876364534337891],[0.17323225313647497,0.17231307297150633,0.1713134465805568,0.1702259854405383,0.1690426550410213,0.1677547619278904,0.16635295434558137,0.16482723992875772,0.16316702426365515,0.16136117452856555,0.15939811285009334,0.15726594450462697,0.15495262669264237,0.1524461843712909,0.1497349806202825,0.1468080503310254,0.14365550776911443,0.14026904091596673,0.13664250863013075,0.1327726607939837,0.12866000694154536,0.12430986554260791,0.11973363404374159,0.11495032818354042,0.10998844574373383,0.10488820925696232,0.09970422219177778,0.09450850939520414,0.08939376011790905,0.08447627840560265,0.07989758311992001,0.07582276116648397,0.07243280972048405,0.06990816783862773,0.06840294186111129,0.06801480526512026,0.06876161190965153,0.07057616387190817,0.07332211276488948,0.07682286591721248,0.08089107329168083,0.08535028972683475,0.09004686524708015,0.09485412697789218,0.09967188227805167,0.10442366019448716,0.10905317836015391,0.11352080149901522,0.11780032144603529,0.1218761619897055],[0.1738039194977483,0.17292169564891388,0.17196073840473353,0.1709138442520206,0.1697732198687142,0.16853047929917425,0.1671766553408768,0.16570222850414504,0.16409717727785478,0.16235105383264437,0.16045308973547637,0.15839233675928183,0.15615784848136346,0.15373890911644308,0.1511253169774627,0.14830773116277854,0.1452780916044279,0.1420301245542742,0.13855994799842397,0.13486679440023383,0.1309538714996277,0.12682938533167937,0.1225077523839153,0.1180110281652744,0.11337057392192926,0.10862896516186414,0.10384210312960274,0.09908140366973192,0.09443577823530441,0.09001285691240501,0.08593852274789242,0.08235340522978407,0.07940478392016627,0.07723290207551209,0.07595254096009832,0.07563370316744847,0.07628771973501962,0.07786448862836692,0.0802621570945009,0.08334518612490402,0.08696421505921069,0.09097245938212023,0.09523645518792916,0.09964147940019408,0.10409309800216547,0.10851637071112563,0.11285387099556009,0.11706325694906397,0.12111480331879723,0.12498909677039784]],[],[]]},{"xaxis.title":"C","xaxis2.title":"C","xaxis.range":[-9.0,6.0],"xaxis2.range":[-9.0,6.0],"xaxis.type":"log","xaxis2.type":"log"}],"label":"C","method":"update"},{"args":[{"x":[[1e-06,1.757510624854793e-06,3.0888435964774785e-06,5.428675439323859e-06,9.540954763499944e-06,1.67683293681101e-05,2.94705170255181e-05,5.1794746792312125e-05,9.102981779915228e-05,0.00015998587196060574,0.0002811768697974231,0.0004941713361323833,0.000868511373751352,0.0015264179671752333,0.0026826957952797246,0.004714866363457394,0.008286427728546842,0.014563484775012445,0.025595479226995333,0.04498432668969444,0.07906043210907701,0.1389495494373136,0.244205309454865,0.42919342601287785,0.7543120063354607,1.325711365590108,2.329951810515372,4.094915062380427,7.196856730011514,12.648552168552959,22.229964825261955,39.06939937054613,68.66488450042998,120.67926406393264,212.09508879201925,372.7593720314938,655.1285568595496,1151.3953993264481,2023.5896477251556,3556.4803062231213,6250.551925273976,10985.411419875572,19306.977288832455,33932.217718953296,59636.23316594637,104811.3134154683,184206.99693267164,323745.754281764,568986.6029018281,1000000.0],[1e-06,1.757510624854793e-06,3.0888435964774785e-06,5.428675439323859e-06,9.540954763499944e-06,1.67683293681101e-05,2.94705170255181e-05,5.1794746792312125e-05,9.102981779915228e-05,0.00015998587196060574,0.0002811768697974231,0.0004941713361323833,0.000868511373751352,0.0015264179671752333,0.0026826957952797246,0.004714866363457394,0.008286427728546842,0.014563484775012445,0.025595479226995333,0.04498432668969444,0.07906043210907701,0.1389495494373136,0.244205309454865,0.42919342601287785,0.7543120063354607,1.325711365590108,2.329951810515372,4.094915062380427,7.196856730011514,12.648552168552959,22.229964825261955,39.06939937054613,68.66488450042998,120.67926406393264,212.09508879201925,372.7593720314938,655.1285568595496,1151.3953993264481,2023.5896477251556,3556.4803062231213,6250.551925273976,10985.411419875572,19306.977288832455,33932.217718953296,59636.23316594637,104811.3134154683,184206.99693267164,323745.754281764,568986.6029018281,1000000.0],[0.0006015170467586964,5357.645905431237,0.008579956814279222,0.00018470757289220898,0.05453675687985037,0.0013744807130274097,1e-06,0.00012518635614469357,1e-06],[0.0006015170467586964,5357.645905431237,0.008579956814279222,0.00018470757289220898,0.05453675687985037,0.0013744807130274097,1e-06,0.00012518635614469357,1e-06],[1e-06,1.757510624854793e-06,3.0888435964774785e-06,5.428675439323859e-06,9.540954763499944e-06,1.67683293681101e-05,2.94705170255181e-05,5.1794746792312125e-05,9.102981779915228e-05,0.00015998587196060574,0.0002811768697974231,0.0004941713361323833,0.000868511373751352,0.0015264179671752333,0.0026826957952797246,0.004714866363457394,0.008286427728546842,0.014563484775012445,0.025595479226995333,0.04498432668969444,0.07906043210907701,0.1389495494373136,0.244205309454865,0.42919342601287785,0.7543120063354607,1.325711365590108,2.329951810515372,4.094915062380427,7.196856730011514,12.648552168552959,22.229964825261955,39.06939937054613,68.66488450042998,120.67926406393264,212.09508879201925,372.7593720314938,655.1285568595496,1151.3953993264481,2023.5896477251556,3556.4803062231213,6250.551925273976,10985.411419875572,19306.977288832455,33932.217718953296,59636.23316594637,104811.3134154683,184206.99693267164,323745.754281764,568986.6029018281,1000000.0],[1e-06,1.757510624854793e-06,3.0888435964774785e-06,5.428675439323859e-06,9.540954763499944e-06,1.67683293681101e-05,2.94705170255181e-05,5.1794746792312125e-05,9.102981779915228e-05,0.00015998587196060574,0.0002811768697974231,0.0004941713361323833,0.000868511373751352,0.0015264179671752333,0.0026826957952797246,0.004714866363457394,0.008286427728546842,0.014563484775012445,0.025595479226995333,0.04498432668969444,0.07906043210907701,0.1389495494373136,0.244205309454865,0.42919342601287785,0.7543120063354607,1.325711365590108,2.329951810515372,4.094915062380427,7.196856730011514,12.648552168552959,22.229964825261955,39.06939937054613,68.66488450042998,120.67926406393264,212.09508879201925,372.7593720314938,655.1285568595496,1151.3953993264481,2023.5896477251556,3556.4803062231213,6250.551925273976,10985.411419875572,19306.977288832455,33932.217718953296,59636.23316594637,104811.3134154683,184206.99693267164,323745.754281764,568986.6029018281,1000000.0],[0.0006015170467586964,5357.645905431237,0.008579956814279222,0.00018470757289220898,0.05453675687985037,0.0013744807130274097,1e-06,0.00012518635614469357,1e-06],[0.0006015170467586964,5357.645905431237,0.008579956814279222,0.00018470757289220898,0.05453675687985037,0.0013744807130274097,1e-06,0.00012518635614469357,1e-06]],"y":[[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],[1e-09,2.0235896477251556e-09,4.094915062380419e-09,8.28642772854686e-09,1.67683293681101e-08,3.3932217718953296e-08,6.866488450042998e-08,1.389495494373136e-07,2.811768697974231e-07,5.689866029018304e-07,1.151395399326448e-06,2.3299518105153717e-06,4.71486636345739e-06,9.540954763499944e-06,1.9306977288832496e-05,3.906939937054621e-05,7.906043210907701e-05,0.00015998587196060574,0.00032374575428176466,0.0006551285568595509,0.001325711365590111,0.002682695795279727,0.005428675439323859,0.010985411419875595,0.022229964825261957,0.04498432668969444,0.09102981779915227,0.18420699693267165,0.3727593720314938,0.7543120063354607,1.5264179671752365,3.088843596477485,6.250551925273976,12.648552168552959,25.595479226995334,51.79474679231223,104.81131341546875,212.09508879201925,429.1934260128778,868.511373751352,1757.5106248547966,3556.480306223136,7196.856730011528,14563.484775012445,29470.517025518096,59636.23316594637,120679.26406393314,244205.30945486546,494171.33613238385,1000000.0],[3.428714353076635e-05,55.38136172368294,690.33938400923,562386.4909845794,923227.2828835016,8059.70102430378,657.4126489790578,410.75370137586805,57567.15135812723],[3.428714353076635e-05,55.38136172368294,690.33938400923,562386.4909845794,923227.2828835016,8059.70102430378,657.4126489790578,410.75370137586805,57567.15135812723],[1e-06,1.757510624854793e-06,3.0888435964774785e-06,5.428675439323859e-06,9.540954763499944e-06,1.67683293681101e-05,2.94705170255181e-05,5.1794746792312125e-05,9.102981779915228e-05,0.00015998587196060574,0.0002811768697974231,0.0004941713361323833,0.000868511373751352,0.0015264179671752333,0.0026826957952797246,0.004714866363457394,0.008286427728546842,0.014563484775012445,0.025595479226995333,0.04498432668969444,0.07906043210907701,0.1389495494373136,0.244205309454865,0.42919342601287785,0.7543120063354607,1.325711365590108,2.329951810515372,4.094915062380427,7.196856730011514,12.648552168552959,22.229964825261955,39.06939937054613,68.66488450042998,120.67926406393264,212.09508879201925,372.7593720314938,655.1285568595496,1151.3953993264481,2023.5896477251556,3556.4803062231213,6250.551925273976,10985.411419875572,19306.977288832455,33932.217718953296,59636.23316594637,104811.3134154683,184206.99693267164,323745.754281764,568986.6029018281,1000000.0],[1e-06,1.757510624854793e-06,3.0888435964774785e-06,5.428675439323859e-06,9.540954763499944e-06,1.67683293681101e-05,2.94705170255181e-05,5.1794746792312125e-05,9.102981779915228e-05,0.00015998587196060574,0.0002811768697974231,0.0004941713361323833,0.000868511373751352,0.0015264179671752333,0.0026826957952797246,0.004714866363457394,0.008286427728546842,0.014563484775012445,0.025595479226995333,0.04498432668969444,0.07906043210907701,0.1389495494373136,0.244205309454865,0.42919342601287785,0.7543120063354607,1.325711365590108,2.329951810515372,4.094915062380427,7.196856730011514,12.648552168552959,22.229964825261955,39.06939937054613,68.66488450042998,120.67926406393264,212.09508879201925,372.7593720314938,655.1285568595496,1151.3953993264481,2023.5896477251556,3556.4803062231213,6250.551925273976,10985.411419875572,19306.977288832455,33932.217718953296,59636.23316594637,104811.3134154683,184206.99693267164,323745.754281764,568986.6029018281,1000000.0],[0.0006015170467586964,5357.645905431237,0.008579956814279222,0.00018470757289220898,0.05453675687985037,0.0013744807130274097,1e-06,0.00012518635614469357,1e-06],[0.0006015170467586964,5357.645905431237,0.008579956814279222,0.00018470757289220898,0.05453675687985037,0.0013744807130274097,1e-06,0.00012518635614469357,1e-06]],"z":[[[0.4768731329347414,0.473373063454019,0.4700235377784523,0.4668479445672137,0.4638688590744131,0.46110758032766674,0.4585836496096847,0.4563143675689019,0.45431433119648906,0.452595014825889,0.45116442052442846,0.4500268221218677,0.4491826232914162,0.4486283436343913,0.44835673820764854,0.44835704641626767,0.4486153569616472,0.4491150678259556,0.4498374149968725,0.45076204120331353,0.451867576243219,0.45313220304394075,0.45453418769892784,0.45605235663547267,0.4576665091515635,0.4593577583458596,0.4611087976606736,0.46290409372340496,0.4647300088798797,0.4665748588089146,0.46842891197577446,0.4702843385224885,0.47213511660434665,0.47397690425436684,0.4758068846686838,0.4776235924200225,0.47942672757596394,0.48121696406562786,0.48299575793648386,0.48476516039967965,0.4865276398002192,0.4882859158865903,0.4900428090094149,0.49180110616454287,0.49356344512500555,0.49533221728879284,0.4971094893140682,0.498896943126677,0.5006958334710466,0.5025069618370067],[0.47552536936071166,0.4718763661183613,0.46838128460010303,0.46506513862023097,0.4619521545932107,0.4590652618060344,0.45642555522196815,0.45405174990171504,0.45195965142963607,0.4501616710611286,0.4486664166503262,0.4474783897933888,0.4465978153698213,0.44602062173517254,0.44573857895299684,0.4457395901157029,0.4460081188566808,0.4465257263832133,0.4472716850138472,0.4482236327581826,0.4493582346423738,0.4506518204343489,0.45208097410424253,0.4536230567540371,0.45525665106138935,0.45696192097098404,0.4587208851490739,0.46051760650384965,0.46233830290430433,0.4641713862118742,0.46600743800903827,0.46783913110536784,0.46966110614958734,0.47146981258229864,0.4732633228147253,0.4750411279825865,0.476803922954431,0.47855338751207666,0.4802919697998293,0.48202267728519904,0.48374887960862945,0.48547412684192415,0.48720198584098084,0.48893589658272646,0.49067904963177245,0.49243428520058896,0.49420401365733174,0.4959901568050874,0.49779410881012776,0.4996167152970518],[0.47454994543099366,0.4707556396922702,0.4671180798260149,0.463663936313104,0.4604191348778763,0.4574082983894525,0.4546541502625612,0.45217689990424037,0.4499936378352924,0.44811777440334327,0.44655856008392614,0.4453207257274702,0.4444042765892695,0.4438044642696201,0.4435119466980534,0.4435131301012911,0.4437906712512149,0.4443241058156597,0.44509056107160894,0.44606550907988746,0.44722351901025786,0.44853897328104186,0.44998671997364087,0.4515426422295303,0.4531841330564096,0.4548904705985023,0.4566430942413391,0.4584257859322291,0.4602247639416993,0.46202869815979575,0.4638286571120054,0.4656179973712689,0.46739220608464466,0.46914870704460526,0.4708866402073509,0.472606623863018,0.4743105078470339,0.47600112528716587,0.4776820494371389,0.4793573611792516,0.4810314318055646,0.48270872472802556,0.48439361883881915,0.4860902553586493,0.4878024091866682,0.48953338501401655,0.4912859377941364,0.493062216585513,0.49486373030189307,0.4966913335238974],[0.4739929085393084,0.47005876666282215,0.4662835670967987,0.46269564762644594,0.45932266230594837,0.4561909748042117,0.4533249996884064,0.4507465130434648,0.44847396311942417,0.4465218206583799,0.44490001525447537,0.443613506249446,0.442662032250267,0.4420400715279507,0.4417370273603764,0.44173763082239226,0.44202253276553394,0.44256904070114306,0.44335194743747786,0.4443443970130579,0.4455187383766755,0.44684732615148554,0.44830323839706504,0.4498608917543587,0.45149654360780656,0.4531886784193868,0.454918281103331,0.4566690043862478,0.4584272398088299,0.4601821036627475,0.4619253499816412,0.4636512229338626,0.4653562607644297,0.4670390629297835,0.46870003135268096,0.470341095861409,0.4719654329145077,0.4735771856837258,0.4751811925002128,0.47678272958333884,0.47838727288679,0.4800002828301849,0.4816270146534397,0.4832723561519866,0.4849406936396232,0.4866358061568106,0.4883607872082461,0.4901179926844571,0.49190901310462964,0.49373466791492127],[0.4739016227380969,0.46983517737276276,0.4659291776805927,0.46221361305695147,0.4587178694683405,0.4554700758176862,0.4524963820347175,0.44982019010108387,0.4474613711320792,0.4454355141402054,0.44375326269083526,0.4424198009051924,0.4414345467379984,0.4407910962230427,0.4404774384727117,0.44047643203574616,0.44076650523261757,0.4413225223621022,0.44211674761304165,0.4431198391013751,0.44430181406480723,0.44563293925341857,0.4470845146801944,0.4486295319092369,0.45024319883163094,0.4519033311087414,0.4535906163363259,0.4552887608995023,0.4569845318887526,0.45866770772650506,0.4603309516317963,0.46196962196887337,0.4635815330593448,0.4651666793093974,0.46672693459805614,0.4682657378468278,0.4697877745845889,0.471298663162138,0.47280465307970226,0.4743123416859412,0.47582841430573874,0.47735941167360996,0.4789115274079281,0.48049043717691436,0.4821011601988967,0.4837479528040784,0.48543423297823973,0.48716253412254396,0.48893448570604287,0.49075081806220955],[0.47432421635242367,0.470135296695335,0.46610758247186335,0.4622726669559672,0.45866163901390977,0.4553043863080964,0.45222881152868893,0.4494599810821809,0.4470192404495538,0.44492334743354384,0.44318369070779984,0.4418056715166204,0.4407883252824245,0.4401242431723007,0.4397998219253495,0.43979582996735855,0.4400882394280905,0.44064924675093153,0.44144839387761725,0.4424537063459652,0.4436327790611185,0.44495375918577573,0.44638619404405955,0.44790172762189057,0.44947464130443276,0.451082243061658,0.45270511497117044,0.4543272324458494,0.4559359704313689,0.45752201264290704,0.45907917997852593,0.4606041938279542,0.4620963892577432,0.46355739210720426,0.46499077294501706,0.46640168965904805,0.46779652921087744,0.4691825578018202,0.47056758738455257,0.47195966512857307,0.47336679112425495,0.4747966683069549,0.4762564873193778,0.4777527478286982,0.47929111669691454,0.48087632238978123,0.4825120841203612,0.4842010734727883,0.4859449056503811,0.4877441570441684],[0.47530890006043885,0.471009850158852,0.46687199377264743,0.46292844287361895,0.4592119199934301,0.4557540246971662,0.45258439254107685,0.44972976195939146,0.4472129820471292,0.4450520165515312,0.44325902337822226,0.44183960780981263,0.44079235193540856,0.44010870419428116,0.43977327033069746,0.4397644901713018,0.44005563078706256,0.4406159915847101,0.44141220706601375,0.4424095444276288,0.4435731164992705,0.44486895671175075,0.44626492610447077,0.4477314404795667,0.4492420185715504,0.4507736604286065,0.4523070702325015,0.4538267405268058,0.45532091604769453,0.4567814555988847,0.4582036100431787,0.459585733729651,0.4609289456827761,0.46223675573590467,0.4635146695486031,0.46476978513564027,0.4660103921724596,0.4672455839394843,0.4684848903355547,0.4697379389407569,0.47101414965563715,0.47232246700616537,0.4736711328046545,0.4750675005218969,0.47651789148224283,0.47802749186770516,0.47960028853317516,0.4812390408115039,0.48294528483719834,0.4847193664462383],[0.4769031469748352,0.4725090168490019,0.4682752996630872,0.46423649919716126,0.4604268548666416,0.45687958055600997,0.45362597485074685,0.45069441141986516,0.44810923770825045,0.4458896380266798,0.44404855131877347,0.44259176607745077,0.4415173300726497,0.4408153942898011,0.44046855281629627,0.4404526578089001,0.44073801128406853,0.441290790250488,0.44207455651725663,0.4430517267347875,0.4441849147033794,0.44543809341543483,0.44677755235374855,0.4481726451429547,0.4495963351127358,0.45102555365069746,0.452441390128303,0.4538291339389522,0.4551781896348144,0.4564818858183964,0.4577371976580292,0.45894440184357543,0.46010668158868784,0.4612296979789512,0.46232114259215684,0.46339028489224665,0.46444752642822007,0.46550397235685703,0.4665710292580616,0.46766003663266276,0.46878193787907074,0.469946994958253,0.47116454940304375,0.47244283083945743,0.4737888127983882,0.4752081143394104,0.4767049449144912,0.47828208899247526,0.47994092626117185,0.4816814827294006],[0.47915273183903595,0.47468142134761837,0.47036901756748295,0.4662512455780474,0.4623636916239913,0.45874102550130075,0.4554160747835349,0.452418750166254,0.44977484057224165,0.44750472901342564,0.4456221263125532,0.44413297181217615,0.4430346861715072,0.4423159495814921,0.44195710047255793,0.4419311257490936,0.44220509906691113,0.4427418667407385,0.44350178865448425,0.44444438801720454,0.44552981852413925,0.44672010283213937,0.4479801275687148,0.4492783993244692,0.4505875768739763,0.4518848003827653,0.4531518407637861,0.4543750929934925,0.45554543687279664,0.4566579878654339,0.4577117595100341,0.4587092576132675,0.45965602505708547,0.46056015462440447,0.4614317857755153,0.46228259979213965,0.463125326142894,0.4639732713085082,0.4648398796368982,0.46573833408307364,0.4666812029416123,0.4676801369239044,0.4687456192013017,0.46988676936797436,0.4711112007167516,0.4724249288102586,0.47383232810696135,0.4753361323980847,0.47693747404701053,0.4786359565056627],[0.48210063511761825,0.47757296546251726,0.4732020612616865,0.46902465662450143,0.46507745904132886,0.4613963671729888,0.45801552510714133,0.454966200903697,0.4522754935037263,0.4499649052718872,0.44804887448402325,0.44653344091443403,0.4454152912467023,0.4446814410795208,0.44430970538110043,0.44426991522120424,0.4445256632944658,0.4450362941562882,0.4457588938094146,0.4466501163868484,0.4476677627714211,0.44877207910016215,0.4499267741495767,0.45109977087714614,0.4522637151266519,0.45339626765488683,0.45448020643208153,0.45550336578270545,0.4564584379664146,0.45734266155059816,0.4581574195433952,0.4589077688089385,0.4596019208043803,0.46025069216850734,0.460866942149671,0.4614650122748766,0.4620601820184462,0.4626681525158232,0.46330456857963975,0.46398458741431575,0.46472250050702396,0.46553141322470387,0.4664229847087938,0.4674072287809844,0.46849237480946276,0.4696847858908265,0.4709889303279364,0.47240740126786174,0.47394097853234257,0.4755887261352086],[0.485785830062194,0.4812255136226994,0.47681932870885807,0.47260477134120255,0.4686193925559691,0.46490002171664035,0.4614818176705358,0.4583971241102489,0.455674115172815,0.45333524493609023,0.4513955755262228,0.4498611668275292,0.4487278470346495,0.44798075102999285,0.44759488019953675,0.44753661833977687,0.4477658593930081,0.44823834139330243,0.4489078873400146,0.44972839125569936,0.4506554854796162,0.4516478788431892,0.4526683807476557,0.45368463691619887,0.45466960646700405,0.45560181074177253,0.45646538376309354,0.4572499530542427,0.4579503781722658,0.4585663728239304,0.45910203491505414,0.45956530735021495,0.45996739085671356,0.4603221285474505,0.460645380347618,0.4609544037698358,0.4612672558094125,0.4616022289257079,0.46197733216417886,0.4624098264555165,0.46291582101800016,0.46350993561892856,0.46420503126986357,0.46501200980093893,0.4659396807522233,0.46699469220624046,0.4681815206297044,0.4695025135450446,0.4709579779455296,0.47254630681259224],[0.49024198680438485,0.4856754642320298,0.4812601383712769,0.4770339976191195,0.47303511758200983,0.4693008954305624,0.4658671115475701,0.46276678609032434,0.46002879919980477,0.45767625845309595,0.4557246472515904,0.4541799126601004,0.45303687567995143,0.45227855031839026,0.45187681812885616,0.4517943484985639,0.45198719315522,0.4524074830919492,0.4530058973279396,0.4537337742666695,0.4545448389635701,0.4553965611636105,0.45625117362110623,0.4570763844646444,0.45784581781271183,0.4585392159417054,0.4591424349469573,0.4596472643289451,0.46005109938278616,0.46035649370090254,0.46057061752633566,0.46070464612036843,0.4607731007303896,0.46079316315254476,0.4607839832602758,0.46076599718774025,0.4607602720850879,0.46078789146993143,0.4608693931633478,0.46102426961140935,0.46127053806744595,0.461624385682806,0.462099892085104,0.4627088295924668,0.4634605389112337,0.4643618760856502,0.4654172246951875,0.46662856589361934,0.4679955978943177,0.4695158959403252],[0.49549614616084614,0.4909522625385481,0.48655656969093464,0.4823472732169697,0.4783626312412478,0.47464019856323003,0.47121590469666763,0.4681229293426902,0.4653903327586328,0.46304139811616934,0.4610916654388715,0.45954673788168726,0.4584002421554714,0.4576328062426606,0.4572128876302126,0.45709924886023034,0.4572440890897508,0.4575960753951562,0.458102983966047,0.45871389352046943,0.45938094700677656,0.46006071657181186,0.4607152103065726,0.46131255879992783,0.4618274181112718,0.4622411242040269,0.4625416323260575,0.4627232732817127,0.4627863569898464,0.46273665214977094,0.46258476924416747,0.4623454725028393,0.4620369448400228,0.46168002815666753,0.4612974597491154,0.4609131238537483,0.4605513355399234,0.4602361721950388,0.4599908656878074,0.4598372659294495,0.45979538398574504,0.4598830201669152,0.46011547971144495,0.46050537588597085,0.4610625176649955,0.46179387675303446,0.46270362667764076,0.4637932450992733,0.4650616694037533,0.46650549507749356],[0.5015674345459793,0.4970769360901087,0.49273179734615413,0.4885701781478474,0.48463017625626437,0.48094907311046725,0.4775624244192294,0.4745029592425938,0.4717992416743398,0.46947403944531624,0.46754233890522207,0.46600897836195904,0.4648661277909765,0.4640917410629191,0.46365060034806055,0.46349753705261737,0.4635810872891847,0.463846758384894,0.46423977274195494,0.46470731086318584,0.46520029634399185,0.46567476618642945,0.4660928677861598,0.4664235219940173,0.46664279002716513,0.46673398058321564,0.46668753214942077,0.4665007040984151,0.466177108676288,0.46572611441573086,0.465162149871454,0.4645039349106029,0.4637736651243955,0.4629961732665691,0.46219808995248185,0.46140702412764734,0.46065078197492393,0.45995664090677946,0.4593506930216705,0.45885726985349806,0.4584984574093896,0.45829370741838543,0.45825954749354725,0.45840938967374134,0.45875343371472993,0.4592986587031675,0.46004889421623696,0.4610049604541353,0.462164865595442,0.4635240480778539],[0.50846590581502,0.5040607560624316,0.49979854223029163,0.49571714200010203,0.4918541689599285,0.488246206726061,0.48492790052167983,0.4819308719854752,0.47928241243301517,0.47700389755454004,0.4751088528601591,0.4736005861917538,0.4724693610281244,0.47169016202144065,0.4712240379391583,0.4710221590700864,0.4710298054755374,0.47118974956848453,0.47144506646906315,0.4717414231848049,0.472028893409553,0.47226334139819726,0.4724074161989318,0.47243119610969836,0.4723125221924593,0.47203705873696133,0.47159811752305286,0.47099628149025474,0.4702388619667719,0.46933922197512956,0.4683159963863756,0.4671922379127227,0.4659945161668931,0.4647519953003816,0.4634955140471081,0.46225669028804794,0.4610670704292787,0.45995734184780723,0.4589566243098455,0.45809185353737447,0.4573872669734681,0.4568639983212828,0.4565397837190325,0.4564287786340456,0.45654148091995983,0.456884752196866,0.45746192697703925,0.4582729969123442,0.4593148562616371,0.4605815941746649],[0.516191600545808,0.5119041385406056,0.5077577831777994,0.503789927692752,0.5000374081943234,0.49653571009028785,0.49331804518632105,0.4904142680842908,0.48784958927036537,0.4856430290807928,0.48380554175485835,0.4823377223147447,0.4812270032115027,0.4804451737282393,0.479949940815264,0.4796893707977884,0.47960600479059057,0.47964033441878373,0.4797336919699619,0.47983060340740397,0.47988064860566126,0.479839870916991,0.4796717771191701,0.47934796837327864,0.47884844257843123,0.4781616081215658,0.4772840482909138,0.47622007448182724,0.47498110480301603,0.47358490288713057,0.47205470975168917,0.4704182995726268,0.4687069883216763,0.4669546224280397,0.46519657294085465,0.46346875901705215,0.46180672281498536,0.4602447758858952,0.4588152347737568,0.45754776064668773,0.45646881434503844,0.4556012342870809,0.4549639403631165,0.45457176249643755,0.45443538823203744,0.45456141982065856,0.45495252805406833,0.45560768776547955,0.4565224785324702,0.4576894337063819],[0.5247339035333387,0.5205958910966301,0.5165978683967777,0.512776577210815,0.5091678157248481,0.5058055991045668,0.5027212045287566,0.49994207287542247,0.49749052726741927,0.49538225453516377,0.4936244804181976,0.49221376234025743,0.4911334539223847,0.49035197416982323,0.48982429680322204,0.48949597983595483,0.4893073257828849,0.4891969718963903,0.489104885473555,0.4889748024578767,0.48875615018056157,0.48840549495418556,0.487887555689717,0.4871758255098398,0.4862528440071441,0.4851101629946756,0.48374804813665806,0.4821749577051966,0.4804068379853151,0.4784662727265962,0.4763815217282939,0.4741854813474326,0.471914597588776,0.469607760548974,0.4673052073327141,0.4650474590348402,0.4628743158128723,0.46082393223763907,0.4589319927804632,0.457231004292999,0.45574971857122054,0.45451269360476104,0.45353999707118053,0.4528470503381335,0.4524446060606042,0.45233884779949385,0.45253159628957734,0.4530206042963439,0.45379992053764984,0.4548603028863818],[0.5340712548186974,0.5301128781796244,0.5262941260396233,0.5226509567858254,0.5192179032596635,0.5160271672575084,0.513107613310765,0.5104836389635032,0.5081738869447125,0.5061897528468087,0.5045336399392224,0.5031969668973295,0.5021582233240591,0.5013821013827731,0.5008209457299145,0.5004181813868485,0.5001122765556397,0.4998403878593123,0.4995414629584831,0.4991587793433573,0.49864194383839916,0.4979483888214899,0.49704440586686305,0.4959057605090965,0.49451793379297676,0.4928760371701638,0.49098444707049826,0.4888562041947596,0.4865122204619375,0.4839803338984017,0.48129424890613104,0.47849239659085385,0.4756167473921972,0.47271160625268316,0.4698224189808258,0.4669946171687858,0.4642725277706208,0.46169837191468766,0.4593113753788564,0.4571470101182907,0.45523638214337797,0.4536057759174331,0.45227635949705147,0.4512640482694825,0.4505795188665057,0.4502283591961199,0.4502113360055822,0.450524758297498,0.45116091339939784,0.45210855248005916],[0.5441712323150064,0.5404201288619975,0.536809005039329,0.5333729436981621,0.5301450252544818,0.527155335051547,0.524429887683414,0.5219894542368277,0.5198482700264542,0.5180125987388903,0.5164791545709055,0.515233490744109,0.5142487326340185,0.5134853830126482,0.5128928236123189,0.512412315938575,0.511980657636867,0.5115337667829059,0.5110098447088437,0.5103520043043402,0.5095103479748964,0.5084435161012215,0.5071197424630692,0.5055174611389952,0.5036255138636511,0.5014430088705064,0.49897888231655396,0.49625121184283155,0.4932863291019248,0.49011777466848216,0.48678513512942023,0.48333279875527524,0.47980866329959093,0.4762628273260246,0.472746295017762,0.4693097235000401,0.4660022409662888,0.4628703628920903,0.45995703186072634,0.4573008035791757,0.4549351972647002,0.4528882227084885,0.45118208924341907,0.4498330940952297,0.4488516798959828,0.44824264424298715,0.44800547874669305,0.4481348114567304,0.4486209250357201,0.44945032344543234],[0.5549909835422764,0.5514713554435998,0.548092700865912,0.5448891877736426,0.5418923161627951,0.5391298184610889,0.5366245004706702,0.5343930235338618,0.532444626900841,0.530779800506744,0.5293889631056192,0.5282513093326076,0.5273341655305684,0.5265933219124701,0.5259746553452953,0.5254169013773913,0.5248550508314948,0.5242238146259345,0.5234607884977863,0.5225091376032122,0.5213197368369828,0.5198527628209989,0.518078764194682,0.5159792532384229,0.5135468706835358,0.5107851796148609,0.5077081450089953,0.5043393535851879,0.5007110250901932,0.4968628616731249,0.4928407773499224,0.48869554531267095,0.4844813974445593,0.4802546080910719,0.47607209291779395,0.4719900533244258,0.4680626969322373,0.46434106449644913,0.4608719925150428,0.457697238162932,0.45485278853392136,0.45236836942765185,0.4502671604052527,0.44856571329006284,0.44727406171571016,0.446396000792623,0.44592950938051157,0.44586728338369347,0.4461973470786218,0.4469037105054727],[0.5664779499685177,0.5632098067956466,0.5600841614383836,0.5571343004130188,0.5543901012634563,0.5518768082945361,0.5496137804812193,0.5476132329511901,0.5458789985000629,0.5444053545423113,0.5431760065371976,0.5421633989874883,0.541328616433767,0.540622159949913,0.5399857475797383,0.5393550149086624,0.5386627556992403,0.5378422796767284,0.5368305493744746,0.5355708872056051,0.5340151513527202,0.5321253506336086,0.5298747122382476,0.5272482420588516,0.5242428318017708,0.5208669739181376,0.5171401468778618,0.5130919310594911,0.5087609108896685,0.5041934130338773,0.4994421244446269,0.4945646287438726,0.489621895345128,0.48467675323023485,0.4797923804154055,0.475030840591822,0.4704516996258669,0.46611075571390426,0.46205891701633406,0.45834125858056146,0.45499628559113453,0.45205542222674533,0.44954273505361736,0.4474748879555617,0.445861313529659,0.4447045751956673,0.4440008862466387,0.4437407474492463,0.44390966370196233,0.4444889022482726],[0.5785708069897875,0.5755693565436515,0.5727123417273489,0.5700322963702528,0.5675575474981237,0.5653108493212575,0.5633080287738943,0.5615566888407162,0.5600550250729128,0.5587908297574768,0.5577407920565202,0.556870247503118,0.5561335629914399,0.5554753197835464,0.5548323442092605,0.5541364605805584,0.5533176884258544,0.5523075477233771,0.5510421730938033,0.5494650243060641,0.5475290710308494,0.5451984029645599,0.5424492684036757,0.5392705782467924,0.535663932473531,0.5316432359399837,0.527233972633925,0.5224722046541095,0.5174033560957131,0.5120808344377508,0.506564534348044,0.5009192621460998,0.4952131142666215,0.4895158403788689,0.48389722141233305,0.4784254943039844,0.47316585809942097,0.46817909901127885,0.4635203737909341,0.4592381898821729,0.4553736161617236,0.45195974915139925,0.44902144685870593,0.44657532727368665,0.44463001310126815,0.44318659077150857,0.44223924194744685,0.44177600060480415,0.44177958830039255,0.44222828370908657],[0.5912005374572622,0.5884757246651835,0.585897581298366,0.5834981329668238,0.5813043654537953,0.5793366973833001,0.5776075089490614,0.5761198000126518,0.5748660609723338,0.5738274533789184,0.572973414286241,0.5722618122919043,0.5716397779173333,0.5710452853131175,0.570409467711998,0.5696595272546221,0.568721996802613,0.5675260661723458,0.5660067045216565,0.564107372835692,0.5617821971520484,0.5589975442605422,0.5557329979611082,0.5519817736540618,0.5477506335494966,0.5430593768076348,0.5379399814345023,0.5324354706480943,0.5265985683252099,0.5204901982909187,0.514177872443305,0.5077340043980845,0.5012341794506459,0.4947554087422387,0.488374395725629,0.48216584604228585,0.47620085691921105,0.470545427788562,0.46525913816923514,0.46039403985354094,0.4559938063063056,0.452093171973702,0.4487176783642179,0.44588372426927986,0.44359889740326275,0.4418625473698313,0.44066654779433007,0.43999618992733497,0.4398311507771092,0.44014648452055044],[0.6042915638752394,0.601847745822633,0.5995530055076567,0.5974392356343241,0.595532443642445,0.5938510376699175,0.5924042143641062,0.5911905503997393,0.5901969084737123,0.5893977739915695,0.5887551383083394,0.5882190327328902,0.5877287858975788,0.587215018060818,0.5866023014972276,0.5858123236660477,0.584767316778036,0.5833934863446453,0.5816241878372841,0.5794026532789871,0.5766841394908832,0.5734374397681794,0.5696457600350135,0.5653070041186756,0.5604335400515074,0.5550515321258934,0.5491999248948718,0.5429291588981772,0.536299686895634,0.5293803466214426,0.522246633751638,0.5149789085333693,0.50766056247432,0.5003761683052341,0.49320963735418544,0.4862424132663895,0.4795517388030556,0.47320904162191885,0.4672784930447831,0.46181579787147475,0.4568672704360337,0.452469240555833,0.44864781310058627,0.44541897935780395,0.44278905180004247,0.44075537127678477,0.43930722083336166,0.4384268748041039,0.4380907147344996,0.4382703527185129],[0.6177628784974724,0.6155986199524959,0.6135858842634552,0.6117569459904973,0.6101373600401628,0.6087440272471275,0.607583404610352,0.6066499925022352,0.6059252384001961,0.6053769936504646,0.6049596432474077,0.6046149951905658,0.6042739631309145,0.6038590046948561,0.6032871957579605,0.6024737432648928,0.6013356845145056,0.5997955031058587,0.5977844140286166,0.5952451244211517,0.5921339475271055,0.5884222200963232,0.5840970362902149,0.579161357566601,0.5736335862293229,0.5675467019333718,0.5609470589832437,0.5538929319865212,0.5464528823677749,0.5387040017735215,0.5307300730431072,0.5226196769605597,0.5144642646230502,0.506356211711016,0.49838687260332204,0.490644659084413,0.48321317959645016,0.4761694888381374,0.4695825109624966,0.46351170847589845,0.4580060686541733,0.45310346658914813,0.448830438655959,0.44520236609038494,0.44222403255685494,0.43989048984896745,0.4381881477701938,0.43709599948324757,0.43658690023464375,0.4366288313368739],[0.631529126104033,0.6296371026524241,0.6278989120179668,0.6263478666732134,0.625009761050068,0.6239006735079479,0.623024948387983,0.6223735240124512,0.6219227791528406,0.6216340601251468,0.6214540194171069,0.6213158431529611,0.6211413710495421,0.6208440259354092,0.6203323824982885,0.619514132079296,0.6183001567994459,0.6166084213228665,0.614367424450603,0.6115190168706355,0.6080204714029823,0.6038457725145834,0.5989861601928097,0.5934500120416641,0.5872621746732914,0.5804628633169103,0.573106241717272,0.5652587782480437,0.5569974536572596,0.5484078748589282,0.5395823303865963,0.5306178082687921,0.5216139872662083,0.5126712083620092,0.5038884356495738,0.49536122457703524,0.4871797305361226,0.47942681045203217,0.4721762908457584,0.4654914920823818,0.4594241030832563,0.45401348762209487,0.4492864708920776,0.44525760861442715,0.44192989169293156,0.43929579973821686,0.4373385950449315,0.4360337463102177,0.4353503842353747,0.4352527123206795],[0.6455016072877627,0.6438686099830417,0.6423913939448016,0.6411051019920518,0.6400366244949849,0.6392020849193086,0.6386045288149352,0.6382320201031421,0.6380563573251828,0.6380326071656801,0.6380996078687216,0.6381815208955206,0.6381904117524656,0.6380297332807167,0.6375984840548823,0.6367957386100355,0.6355252089773644,0.6336995051005804,0.6312438125733206,0.6280987885937626,0.6242225742571956,0.6195919154006715,0.6142024607105319,0.6080683565785983,0.6012212819739694,0.5937090674093503,0.5855940267053598,0.5769511058527637,0.5678659258375967,0.5584327700697076,0.5487525446350942,0.5389307223832221,0.5290752706228414,0.5192945575038792,0.5096952346630462,0.5003801041483585,0.4914459964465989,0.4829817128215168,0.4750661157094249,0.4677664783105746,0.461137217862123,0.45521912532666853,0.45003916256967175,0.44561083354274533,0.441935066599412,0.43900149143375833,0.4367899689290669,0.4352722356394314,0.4344135477299085,0.43417424053691983],[0.6595891784878973,0.6581962223823565,0.6569603348224883,0.6559194057642489,0.6551024349168366,0.6545266396968182,0.6541947725353527,0.6540928949428492,0.6541888711855794,0.6544318278283636,0.6547527685995074,0.6550664368271488,0.6552743905160434,0.6552691178833844,0.6549388982226825,0.6541730266990007,0.6528669872798456,0.6509271806153143,0.6482748876181785,0.6448492593010331,0.6406092471469531,0.6355345029417072,0.6296253646422281,0.6229020966950619,0.6154035700283067,0.6071855562999744,0.5983187832030393,0.5888868623293495,0.5789841654097108,0.5687136929823842,0.5581849537494623,0.547511853732223,0.5368105819465974,0.5261974738781515,0.515786836222184,0.505688727484295,0.496006710761716,0.486835628232853,0.47825948943919483,0.4703496091308972,0.4631631592719036,0.4567422938055621,0.45111395160653106,0.4462903510795916,0.4422700894290343,0.43903968625363926,0.43657538419155506,0.4348450347243371,0.4338099367493346,0.43342654056747165],[0.6736990282032964,0.672521575245121,0.6715014295748142,0.6706802494582205,0.6700903001443572,0.6697511172784423,0.669666361754523,0.6698211628336591,0.6701802751944235,0.6706873636426184,0.671265662408459,0.6718201319982682,0.6722410702665003,0.6724089555147975,0.6722001432383806,0.6714929342703704,0.6701734980059562,0.6681411740673325,0.6653127801916916,0.6616257021971075,0.657039703541982,0.6515375355624394,0.6451245311764855,0.6378274153187745,0.6296925696013911,0.6207839605032061,0.6111808955022793,0.6009757227472323,0.5902715451238623,0.5791799826357257,0.5678189887408154,0.5563107061152681,0.5447793343834761,0.5333489762321407,0.522141429528412,0.5112739033953045,0.5008566588013119,0.49099061273707956,0.4817650007981691,0.4732552592290821,0.46552134280401863,0.45860670426510525,0.45253809491290686,0.44732621134360073,0.4429670631657639,0.439443835288518,0.4367289953741751,0.4347864358994412,0.4335735049363715,0.4330428417427073],[0.6877373073999765,0.686745620160711,0.685909948905997,0.6852768166967076,0.6848830300319383,0.6847518291325954,0.6848891805341768,0.6852805629571239,0.6858886493389273,0.6866522901975077,0.6874871309444189,0.6882880398425232,0.688933303925867,0.6892903128432737,0.689222247828337,0.6885951644678705,0.6872848226746209,0.6851826772580957,0.6822005860447223,0.6782739926227688,0.6733635556210944,0.6674553797219894,0.6605601217894591,0.6527112892573105,0.6439630305281171,0.6343876629911591,0.6240731169231739,0.6131204091315337,0.601641206663057,0.5897555001985679,0.5775893776719752,0.5652728689140106,0.5529378196349398,0.5407157466082718,0.5287356256072758,0.5171215714204601,0.5059903895188875,0.4954490187098155,0.4855919510323933,0.4764988094760505,0.46823236276638835,0.4608373014427972,0.4543400231439454,0.44874947192429965,0.4440588429424654,0.44024782413092556,0.4372850425589903,0.43513046594345556,0.43373761028952235,0.43305548425047974],[0.7016095877031039,0.700769232381873,0.7000815013967495,0.6995989153897919,0.69936418221625,0.6994057697676017,0.6997335329526145,0.7003348010845809,0.7011714201273636,0.7021782763879832,0.7032637590318613,0.7043124245839557,0.7051898328462721,0.7057492032583682,0.7058392757656287,0.7053126022504806,0.7040334583051103,0.7018846477610937,0.6987726634032867,0.6946309370776782,0.689421202309727,0.6831332306968813,0.6757833390605861,0.6674120906033264,0.6580815598139989,0.6478724396527291,0.636881174490487,0.6252172218124127,0.6130004854078853,0.6003589210396589,0.5874262881481702,0.5743400036827432,0.5612390433463013,0.5482618294210588,0.5355440424545745,0.5232162979541005,0.5114016434840802,0.5002128657924351,0.4897496676414764,0.48009589603421154,0.4713171671201171,0.46345935467967064,0.4565483397592291,0.450591102183421,0.4455778537961695,0.44148472472736955,0.4382765666639835,0.43590959682111546,0.4343337507703864,0.43349470338003465],[0.7152211162802317,0.7144936293256167,0.7139126366744671,0.7135377771905574,0.7134190554904745,0.7135917845803297,0.714071449045013,0.7148489442814964,0.7158867880698054,0.71711698793164,0.7184412013289339,0.7197335869484867,0.7208463427918695,0.7216174854641352,0.7218800818745913,0.7214719607578477,0.7202448979983366,0.7180723718271084,0.7148552253954409,0.7105249362396354,0.7050445916530382,0.6984079850749246,0.6906373993304394,0.6817806302966752,0.6719076923441737,0.6611075052502766,0.6494847362829557,0.6371568773861207,0.6242515749471872,0.610904190962984,0.5972555515230832,0.5834498251627194,0.5696324656527224,0.5559481488041019,0.5425386299529589,0.5295404486539188,0.5170824131534264,0.5052828186156841,0.494246411039649,0.48406124235747283,0.47479580557570816,0.46649711240225483,0.45919037467312357,0.45288043992032617,0.44755447274542437,0.4431851411765191,0.43973376323372654,0.4371531480229671,0.43539004655697694,0.4343872124677258],[0.7284768356622765,0.7278205559759814,0.7273012361769614,0.7269866873574166,0.7269355787686546,0.7271917163869984,0.727778061479422,0.7286909765767523,0.729895395173224,0.7313217920201459,0.7328658488051656,0.7343914250454268,0.7357368725701513,0.7367241058677289,0.7371694093477552,0.7368947810179688,0.7357385929840168,0.7335644501964883,0.7302674057539045,0.7257771749077319,0.7200585594282882,0.7131097258450351,0.7049591343184668,0.6956618237112001,0.6852955540894676,0.6739571032155445,0.6617588593006118,0.6488257532499642,0.63529251640517,0.6213012190606648,0.6069990292846055,0.5925361235000772,0.5780636756865205,0.563731848724168,0.5496877083407059,0.5360729773160147,0.5230215465080876,0.5106566651765235,0.49908776323963167,0.4884069641505689,0.47868564253091306,0.46997191303229296,0.46229018944693573,0.4556431107891435,0.4500149117992595,0.4453751197641601,0.44168197767368045,0.43888540925565417,0.4369295147761595,0.43575463952947846],[0.7412811463327038,0.7406521929035255,0.7401466250979267,0.739841361080471,0.7398050041917122,0.7400914454821954,0.7407329875435499,0.7417334790215118,0.7430622287520943,0.7446497924044208,0.746386893684843,0.7481274317715264,0.7496956735417479,0.7508967986391895,0.7515294614003083,0.7513989420693344,0.7503294796880109,0.7481744155283173,0.7448230275063179,0.7402035827874296,0.7342829919185778,0.7270640593165675,0.718581440248406,0.7088971681168228,0.6980962764044244,0.6862827689885115,0.6735760243153809,0.6601076290458969,0.6460185937900992,0.6314568849279993,0.61657519920203,0.6015289049685553,0.5864740724295726,0.5715655133467414,0.5569547480519562,0.5427878138304882,0.5292028241677119,0.516327184173572,0.5042743697783594,0.4931402183234669,0.48299890821880587,0.47389962823883,0.4658659216034553,0.458898333480681,0.4529785789523699,0.4480736538355894,0.4441394120391223,0.44112357592692564,0.4389682372888991,0.4376119167189814],[0.7535374177478389,0.7528907618762405,0.7523493433991445,0.7519999659327075,0.751922273823351,0.7521816803160376,0.7528215835219728,0.7538553292844077,0.7552586949006661,0.7569641714828653,0.7588588133802092,0.7607871900477773,0.762559619411651,0.7639643808852525,0.764782123897874,0.7648008975126995,0.7638303238465556,0.7617132621947645,0.7583333748095582,0.7536178733134185,0.7475361096700346,0.7400955710768451,0.7313367976984314,0.7213282060057766,0.7101612898818461,0.6979463595696349,0.6848088270389809,0.6708859837399174,0.6563241950579983,0.6412764305810058,0.6259000494794268,0.6103547613498492,0.5948006831011521,0.5793964113781088,0.5642970275273604,0.5496519482248912,0.5356025295963898,0.5222793259553931,0.509798896376386,0.4982600463536191,0.48773944149544013,0.4782872982229159,0.46992637113261027,0.4626556069558651,0.45645500963515767,0.451289939092336,0.4471147249875769,0.4438756787903411,0.44151358829504544,0.4399657688606201],[0.7651473074956259,0.7644378564986576,0.7638105550603882,0.7633627074876255,0.7631859112436318,0.7633582989658498,0.7639358525641632,0.7649432167240928,0.7663646934499885,0.7681367202214205,0.7701442143090884,0.7722233781819788,0.7741712634155689,0.7757598282417059,0.7767520999380184,0.7769189570374164,0.7760552405929549,0.7739932711818274,0.7706113588060812,0.7658360384191404,0.7596392077573697,0.7520326676248054,0.7430620485066782,0.7328010858232555,0.721346551152939,0.7088138653201332,0.6953333245514908,0.6810468478645684,0.6661051538250745,0.6506652799857778,0.6348883628877512,0.6189375990055812,0.602976307434316,0.5871660137743842,0.5716644718616616,0.5566235358647169,0.542186789845847,0.528486835069979,0.5156421269897307,0.5037532437351313,0.49289845609284016,0.4831288317122625,0.4744668812130824,0.4669110275382628,0.4604407171323063,0.4550207406827457,0.45060485224838526,0.4471387848906708,0.4445627483237511,0.4428134830345551],[0.7760100315157435,0.7751936229201642,0.7744311785534262,0.7738309872348719,0.7734973415570677,0.7735220261439537,0.7739746999407962,0.7748926364258576,0.7762703730932538,0.7780502739289045,0.7801168222191945,0.7822991943475007,0.784382636698714,0.7861244164389551,0.7872713765470207,0.787578100843674,0.7868249047319983,0.7848336454691958,0.7814775726430966,0.7766827357330358,0.7704231813609416,0.7627139984584018,0.7536044990303699,0.74317219496129,0.7315176199870322,0.7187598966444259,0.7050329302753594,0.690482123429924,0.6752615173655878,0.6595312766849757,0.643455438102063,0.6271998458796629,0.6109301957129122,0.5948101065054118,0.578999136006479,0.5636506517814942,0.5489094634223796,0.5349091151286316,0.5217687297075208,0.5095892867835291,0.49844924178510963,0.488400080023506,0.47946525479641877,0.4716440782535626,0.464916703283362,0.4592484596279786,0.45459349366933005,0.45089780340057284,0.44810175363899646,0.446142145952044],[0.7860218301439027,0.7850560553864984,0.7841110046381504,0.7833063614139523,0.7827597611939046,0.7825773714365223,0.7828432210167416,0.7836078797961954,0.7848770357417135,0.7866005200453622,0.7886641405517603,0.7908919425513449,0.7930599004837094,0.7949134008044095,0.79618570959187,0.796617064076115,0.7959741630612556,0.7940686199870938,0.7907688204997196,0.7859999886768952,0.7797370261111722,0.7719964302585354,0.7628291689309481,0.7523146040094386,0.7405553018849746,0.727672573616312,0.7138026195739527,0.6990931789038933,0.6837005999132691,0.6677872551633159,0.6515192272667704,0.6350641903756594,0.6185894096346388,0.6022597772939552,0.586235800045858,0.5706714475073111,0.555711766645879,0.5414901619687206,0.5281252405282137,0.5157171487703557,0.5043435283703604,0.4940560742702309,0.4848798910593667,0.47681637636739155,0.46984760170261275,0.46394053654292494,0.4590506930769494,0.45512518753509174,0.45210528443762604,0.4499284941007802],[0.7950759632289258,0.7939208159202291,0.792748304296835,0.7916898942241011,0.7908771720867125,0.7904312948821581,0.7904510863084447,0.7910005453898563,0.7920964155235879,0.79369630953837,0.7956890092101107,0.7978964801021793,0.8000890763325702,0.8020038998762679,0.8033641003929339,0.8038987144867848,0.8033629570457864,0.8015588323127779,0.7983496732086671,0.793658331217268,0.7874580417601649,0.7797640584016731,0.7706265833400975,0.7601247325446553,0.7483613282508824,0.7354583700786934,0.7215530780357595,0.706794425796847,0.6913400943058828,0.6753537784485727,0.6590027773324552,0.6424557944321112,0.6258808691112544,0.6094433564986306,0.5933038685606822,0.5776160856816231,0.562524346179681,0.5481609251644666,0.5346429391191801,0.5220689089923275,0.5105153104967397,0.5000340326461233,0.49065200862896663,0.482373357740955,0.47518299603973213,0.46905051144536875,0.46393370801064654,0.45978165956885103,0.4565372765714517,0.4541394347835983],[0.8030635934118482,0.8016820658990602,0.8002406328766785,0.7988828906329231,0.7977548754717939,0.796993166912294,0.7967115881460503,0.7969874281597463,0.7978479266962545,0.7992577624010346,0.8011101759340947,0.8032290917088366,0.8053832714955819,0.8073052694471503,0.8087118532585886,0.8093247769240264,0.8088915658092222,0.8072066583903471,0.8041269017627362,0.7995694288879938,0.7935024268128005,0.7859369561958044,0.7769199775553474,0.766528310328213,0.7548633372500033,0.7420463330494986,0.7282143382393368,0.7135165186272727,0.6981109554949918,0.6821618071219953,0.6658367748219896,0.6493047990844291,0.6327339051701941,0.6162891129765995,0.6001303233200497,0.5844100928087038,0.5692712151791619,0.5548440468408304,0.5412435695573397,0.5285663166205206,0.5168875478492335,0.5062593741564541,0.49671056019192195,0.48824817310028834,0.4808605097247843,0.4745204990656504,0.46918901720857986,0.46481785797480585,0.4613522870288067,0.45873318824025905],[0.8098759500279112,0.8082348796677312,0.8064876357151807,0.80479009428328,0.8033029739052471,0.8021783844707339,0.8015450396945203,0.8014932023279688,0.8020602670977938,0.8032183047039622,0.804866654376139,0.8068341147223139,0.8088914470497244,0.810770253856242,0.8121846236939729,0.8128530488717676,0.8125195115685135,0.8109734600494928,0.8080633101849375,0.8036967479396053,0.7978335106008366,0.7904776113146739,0.7816704226619108,0.771484550155727,0.7600183605877,0.7473910851992148,0.7337384533121646,0.7192088220109064,0.703959760992046,0.6881550386232628,0.6719619420950085,0.6555488543132199,0.6390830036049415,0.6227282992651938,0.606643166621731,0.5909783011745121,0.5758742769217308,0.561458978924449,0.5478449016871331,0.5351264832055734,0.5233778246105594,0.5126512903497737,0.5029774218432416,0.4943662524976389,0.4868096922063188,0.4802844518544742,0.4747550499487082,0.47017662300058605,0.46649741436397224,0.46366090812085203],[0.8154087822613033,0.813480096336799,0.8113964848856667,0.8093258842269825,0.807443501164117,0.8059166333053993,0.8048884667649013,0.8044619969052734,0.8046851312155512,0.8055386367732565,0.8069297017066406,0.8086940387938868,0.810607178754112,0.8124029279672607,0.8137960507251933,0.814505215536643,0.8142734650399649,0.8128860962718655,0.8101825954608507,0.8060591865366081,0.800464520707151,0.7933930952024264,0.7848785942690901,0.7749876666697517,0.7638142092320781,0.7514741685450952,0.7381008701788878,0.7238408711490658,0.708850307475387,0.6932916844775661,0.677331038833472,0.6611353898452885,0.644870392074858,0.6286981015424681,0.612774773030802,0.5972486185234602,0.5822574809200902,0.5679264205631351,0.5543652839569279,0.5416664269178862,0.5299028760981215,0.5191272703365691,0.5093718478488651,0.5006495261405584,0.4929558673430784,0.4862715741347892,0.48056516497789314,0.47579557227531494,0.4719145158879624,0.46886858726996633],[0.819569274898239,0.8173315980582213,0.8148896929477253,0.8124229043487302,0.8101201287071904,0.808162925135507,0.8067082222655502,0.805871626837347,0.8057123494768063,0.8062214238214198,0.8073156216269809,0.8088393136606425,0.810574995709834,0.812261305720492,0.8136162356417204,0.8143606103590448,0.8142373657608803,0.8130277577913327,0.8105625493154673,0.8067261717141512,0.8014549868230052,0.7947323904703062,0.7865827994844823,0.7770654735109579,0.7662685633985221,0.7543035778767028,0.7413003726493225,0.727402700917138,0.712764310269433,0.6975455317697391,0.6819102833738507,0.6660233985260734,0.6500481883611,0.634144150130668,0.6184647448544315,0.6031551853120467,0.5883502047507276,0.5741718214656867,0.5607271771756629,0.5481066020723364,0.5363821244983146,0.5256066597143374,0.5158140456361907,0.5070199497629808,0.49922350995366604,0.4924094649695593,0.48655051044304076,0.48160966175526576,0.4775424763536041,0.4742990537506425],[0.8222843285139483,0.8197249537146071,0.8169142555834187,0.8140417703908118,0.8113084249522702,0.8089083399870393,0.8070110140270673,0.8057444378748789,0.8051799444798549,0.8053203472342094,0.806093611094506,0.8073542433718844,0.8088933574434449,0.8104565075953654,0.8117666856274409,0.812547351376136,0.8125412980756922,0.8115258438338224,0.8093236274613252,0.8058078964224932,0.8009027649919955,0.7945800083443503,0.7868539462238354,0.7777754927483523,0.767426049900564,0.7559116670657477,0.7433577041279561,0.7299040942084944,0.7157012050823008,0.7009062414535359,0.6856801025384374,0.6701845998710143,0.6545799415502465,0.639022397571521,0.6236620754796719,0.6086407572936423,0.5940897794462388,0.5801279789170681,0.566859779411917,0.5543735434157857,0.5427403523772667,0.5320133760762521,0.5222279388890356,0.5134022937821531,0.5055390081288529,0.49862678856127224,0.4926425460963406,0.4875535221463684,0.48331934002322297,0.4798938949347551],[0.8235099685098547,0.8206269297817768,0.817451266265002,0.8141804901098548,0.8110247274676972,0.8081880851056316,0.8058509036824534,0.8041529826879952,0.8031783426718848,0.8029428764670308,0.803387148192888,0.8043769469222585,0.8057130316329733,0.8071489868413958,0.8084136867098646,0.8092335678184257,0.809351372410177,0.8085408829577665,0.8066175245786568,0.8034444579822576,0.7989343669590445,0.7930477484388299,0.7857887355941896,0.777199473507382,0.7673539409448012,0.7563518754669817,0.7443131789748557,0.7313729530916068,0.7176771732914154,0.7033789399922807,0.6886352159716723,0.673603952643937,0.6584415123938023,0.6433003056956046,0.6283265788497095,0.6136583111420897,0.599423209776375,0.58573682676334,0.5727008611103287,0.5604017448716454,0.5489096313867228,0.5382778961749192,0.5285432198395674,0.5197262554343667,0.5118328100459697,0.504855414695242,0.4987751318649286,0.4935634557885654,0.4891841868474842,0.4855951954833728],[0.8232420874042436,0.82004588316012,0.8165253705018622,0.8128822165690226,0.8093318611837279,0.8060851593785889,0.8033310042700378,0.8012198501221107,0.799848418733419,0.7992465620580969,0.7993685118673794,0.8000920138942877,0.8012277960485743,0.8025377687141292,0.8037572212442757,0.8046163933317149,0.8048587962046074,0.8042556323601,0.8026163579008111,0.7997954248343353,0.795695317765387,0.7902661518998734,0.7835023505499521,0.7754373201891982,0.7661372394806807,0.7556948462058394,0.7442236995791599,0.7318530884555072,0.7187235930467178,0.7049832364743519,0.6907841367609363,0.6762795655231133,0.6616213259211344,0.6469573750226949,0.6324296332432192,0.6181719456669315,0.6043081865882971,0.5909505282838949,0.5781979245838198,0.5661348835214408,0.5548306137356873,0.5443386198157305,0.5346967906183075,0.525927977504746,0.5180410087335858,0.5110320456466604,0.5048861649145497,0.49957905040407036,0.4950786932889859,0.4913470223388645],[0.8215286025929817,0.8180422165898517,0.8142119236673397,0.8102388719168767,0.8063395872579644,0.8027280755210526,0.7995989084219485,0.7971111808331122,0.7953733373962101,0.7944292572851155,0.7942473538678941,0.7947174333028779,0.7956600342508205,0.7968456322273142,0.7980168161919728,0.7989090203624014,0.7992680784799338,0.7988642011215923,0.7975025077107989,0.7950303346321286,0.7913414048637324,0.7863766523462398,0.7801216185875529,0.7726012898281953,0.7638738574396878,0.7540244899477012,0.7431595987810788,0.731401738977215,0.7188851431940111,0.7057518305732977,0.6921482111270224,0.6782221024170985,0.6641200807234965,0.6499851003353432,0.6359543305975881,0.6221571801191921,0.6087135001962245,0.5957319833335533,0.5833087947981601,0.5715264911564526,0.5604532850117815,0.5501427061798663,0.540633686116683,0.5319510587802393,0.5241064350766247,0.5170993781926652,0.5109187895471174,0.5055444115631611,0.5009483617445246,0.49709662821962647],[0.8184742146323478,0.814730538478852,0.8106357529329192,0.806386935666228,0.8021977511396925,0.7982816121796615,0.7948353588807235,0.792023710174197,0.7899644122159285,0.7887139895736391,0.7882546750463373,0.788487961514548,0.7892441944267365,0.7903033857686126,0.7914170343251864,0.7923276983453097,0.7927855811783207,0.792561960569244,0.7914596190217026,0.7893205878624003,0.7860313785745153,0.7815250823837447,0.7757793318441947,0.7688110881917924,0.7606704180935595,0.7514344187668452,0.7412016377153074,0.7300870736787207,0.7182177570647267,0.7057288673469124,0.6927603256420435,0.6794537944956259,0.6659500194674312,0.6523864558274198,0.6388951369173098,0.625600757274897,0.6126189621386836,0.600054853636251,0.58800174029442,0.5765401674246383,0.5657372684564121,0.5556464695875913,0.5463075625859631,0.5377471362777793,0.5299793312977432,0.5230068605835636,0.5168222240168395,0.5114090411587019,0.5067434302956311,0.5027953724495665],[0.8142253922201971,0.8102653067521226,0.8059579178966036,0.8014943064727208,0.7970823263534551,0.7929313937598255,0.7892370484158995,0.7861659451540843,0.783841345255066,0.7823289367087698,0.7816227377748994,0.7816355078345503,0.7822086686878165,0.7831338757353961,0.7841737205506032,0.785080068131861,0.7856097186442825,0.7855373042629668,0.7846655663543145,0.782833340709792,0.7799216231172271,0.7758570312682922,0.7706101690877456,0.7641902242375236,0.7566389604000472,0.7480249668126862,0.7384383342279142,0.7279858254394522,0.716786554709108,0.704968154886578,0.692663390179158,0.6800071631477133,0.6671338636938158,0.6541750132802302,0.6412571676310127,0.6285000541949359,0.6160149352147982,0.603903201567956,0.5922552145573986,0.5811494203266855,0.5706517626502792,0.5608154135642828,0.5516808282036152,0.5432761125062822,0.5356176735434575,0.5287111057986391,0.5225522556071142,0.5171284015245372,0.5124194903545473,0.5083993754781684],[0.8089510238160845,0.8048213003572744,0.800357192546578,0.7957427415008582,0.7911780587661563,0.7868658336850296,0.7829969976045824,0.7797363400471897,0.7772082964238012,0.7754827995755519,0.7745612762546392,0.7743679309425792,0.7747580747003211,0.775537598673001,0.7764824582310799,0.7773559823974066,0.7779237650469509,0.7779661079822229,0.7772881570718658,0.7757280233234842,0.7731632857801913,0.769515371788683,0.7647483262242677,0.7588636017647457,0.7518944911453644,0.7439007607188334,0.7349636168197996,0.7251810806779108,0.7146638022742169,0.7035313102874223,0.6919086736961876,0.6799235390086963,0.6677035034656174,0.6553737870009265,0.6430551725604923,0.6308621940343149,0.618901562035778,0.607270828456285,0.5960572994498752,0.5853372116458598,0.5751751867090324,0.5656239743713605,0.556724484276635,0.5485060939927395,0.5409872066765793,0.5341760196033225,0.5280714560941377,0.5226642093672826,0.5179378475265346,0.5138699334787757]],[[0.135431023977963,0.13284603403929068,0.13031107723175817,0.127862435417987,0.12553968487819647,0.12338478268080953,0.12144076926028123,0.11975008997213155,0.11835259510343854,0.11728334771869588,0.11657043848881897,0.11623305601599469,0.11628006861035556,0.11670932564003741,0.11750778705215086,0.11865246119565148,0.12011200812071916,0.12184878024061636,0.12382104180024961,0.125985130720521,0.12829738414250244,0.13071572039189205,0.13320083664617796,0.13571703255603726,0.13823270231556492,0.1407205532336404,0.14315761211873393,0.1455250763986428,0.14780805866410282,0.14999526389408593,0.15207862957226423,0.15405295102643587,0.15591550788709055,0.1576657025432484,0.15930471770422203,0.16083519743423424,0.16226095409124391,0.16358670227371733,0.16481781999360468,0.1659601367177834,0.16701974755135165,0.16800285259816286,0.16891562037244617,0.16976407401357507,0.1705539989515315,0.1712908705718471,0.17197980033243296,0.1726254986930077,0.17323225313647492,0.1738039194977483],[0.1318260344567475,0.12896816257381563,0.12615375201067255,0.12342342004041733,0.12082221264611175,0.11839866885669774,0.11620337427430429,0.11428697259828896,0.1126976796748466,0.11147844922360137,0.11066405517417302,0.11027844918712823,0.110332782840476,0.11082442230998228,0.11173712989615128,0.11304238028352691,0.11470158309486213,0.11666885546655104,0.11889395657866576,0.12132505002864379,0.12391106425829997,0.1266035360778866,0.12935791882871853,0.13213440205519228,0.1348983238395753,0.13762026723665902,0.14027592730900101,0.14284582263120923,0.1453149100401806,0.14767214692198488,0.14991003289968793,0.1520241528615999,0.15401273574064792,0.15587623797550587,0.15761695673948967,0.1592386754228063,0.16074634216397501,0.16214578117933542,0.16344343602870276,0.16464614362540372,0.1657609376370599,0.16679487984988187,0.1677549180303877,0.16864776878133947,0.16947982383608867,0.17025707816213762,0.17098507815381805,0.17166888809440115,0.17231307297150628,0.1729216956489139],[0.12812197173835246,0.12497211545285607,0.12185581001427863,0.11881811149887637,0.11590993997908891,0.11318720004017488,0.11070923570689023,0.10853652548389153,0.10672761809904002,0.10533546214206131,0.10440347340031388,0.10396185953692037,0.1040248062824607,0.10458905615785773,0.10563416896272423,0.10712441044772174,0.1090118922096194,0.11124039188166288,0.11374926197446568,0.11647695615973595,0.11936388913283606,0.12235452871812647,0.1253987540735744,0.12845259089211078,0.13147846289947437,0.13444509549479192,0.13732718762711915,0.1401049429208714,0.1427635269476177,0.14529249722258852,0.14768523671429443,0.14993841006787278,0.15205145361932387,0.1540261048163099,0.15586597314874598,0.15757615255391125,0.1591628740571763,0.1606331968167613,0.1619947355257975,0.1632554221225002,0.16442329985577417,0.16550634787354926,0.16651233459783044,0.16744869819890656,0.16832245247298397,0.16914011636651516,0.1699076652889967,0.17063050223151788,0.1713134465805568,0.17196073840473353],[0.12434568413701097,0.12088615988019889,0.11744621868205142,0.11407525161641634,0.11083028908844728,0.10777530732725138,0.10497969466736108,0.10251567475176095,0.1004545887158494,0.0988621507900679,0.09779310067954605,0.09728600411973287,0.09735915707172907,0.09800848087384882,0.09920790644590094,0.10091215480548943,0.10306126929949606,0.10558595846539265,0.10841283443372383,0.11146889030050325,0.11468489422713044,0.11799766172256128,0.12135134551457966,0.12469795857283844,0.1279973515499889,0.13121683478080393,0.1343305915049131,0.13731898698272105,0.14016784353953735,0.14286772554603974,0.1454132600048601,0.14780250613856655,0.1500363795443327,0.1521181317512672,0.1540528833695064,0.15584720772365743,0.15750876140705947,0.1590459582291357,0.16046768332089806,0.1617830445571593,0.16300115884681024,0.1641309711722569,0.1651811044919892,0.1661597387439358,0.16707451720564523,0.1679324783962669,0.16874001156872567,0.16950283366680224,0.17022598544053832,0.17091384425202058],[0.1205292535178602,0.11674487617697367,0.11296132739976142,0.10923192300562337,0.10561974715870802,0.10219734429625252,0.09904540114412981,0.09625004236876963,0.09389844749172137,0.09207276654822331,0.09084279747398137,0.09025849536691481,0.09034385211216275,0.09109368110886876,0.09247420253222453,0.09442726158807607,0.096877031653767,0.09973760277327678,0.10292002458328893,0.1063379178621189,0.10991135874388994,0.11356916206249552,0.11724989681603895,0.12090200843963901,0.12448337469346185,0.12796054305266452,0.13130782041682165,0.13450632397811682,0.1375430573923834,0.14041004646590174,0.1431035496780582,0.14562334760065665,0.1479721090244757,0.15015482851063647,0.15217832890805008,0.1540508223138816,0.15578152348913316,0.1573803105528964,0.15885742866388522,0.1602232332308137,0.16148796989872435,0.16266158909584993,0.16375359327966796,0.16477291519558157,0.1657278254763766,0.16662586779586816,0.16747381958411123,0.16827767605595814,0.1690426550410213,0.1697732198687142],[0.11670991868715878,0.11258937078215366,0.10844545572879566,0.1043345814588668,0.10032536834658627,0.09649900971649546,0.09294851209693682,0.08977618524184816,0.08708874051965752,0.08498963446803132,0.08356901171569273,0.08289270791080369,0.08299282499998963,0.08386263625397243,0.08545751264822607,0.08770155225623329,0.09049776958545222,0.09373903574420792,0.09731752484000258,0.1011315610950374,0.10508977697520963,0.10911306948529548,0.11313501344360335,0.1171013258925436,0.12096882538208821,0.12470417948895712,0.12828261645065633,0.13168669626382148,0.13490518602581353,0.13793205472798453,0.14076558665259098,0.1434076046689902,0.1458627916138671,0.14813809744853745,0.15024222075209348,0.152185154601545,0.15397778859215586,0.15563156042638351,0.15715815201449332,0.15856922630976064,0.15987620210833317,0.16109006476543355,0.16222121122214034,0.1632793279233617,0.16427330017461464,0.16521115128061384,0.16610000948751358,0.16694610037077107,0.1677547619278904,0.16853047929917425],[0.11292962821058214,0.1084671272542052,0.10395117810851891,0.09943990999164047,0.09500629564826424,0.09073954379630049,0.08674541914337466,0.08314453778224452,0.08006743046076502,0.07764528480811538,0.07599620350075015,0.07520876328356477,0.07532699584848125,0.07634195338414197,0.07819324413378682,0.08077989566038889,0.08397632300688333,0.08764829946019081,0.09166545825263211,0.09590921113326821,0.10027662987411068,0.10468147913027635,0.10905355278882993,0.11333716562121411,0.11748933670164219,0.12147796244847907,0.12528012355570894,0.12888058127809668,0.13227047169553005,0.13544618441460293,0.13840840350678266,0.14116128675310988,0.14371176081848003,0.14606891288933888,0.14824346260618437,0.1502473013395494,0.15209308878223976,0.1537938993705633,0.15536291316806136,0.15681314753741996,0.15815722719441694,0.15940719109799226,0.1605743351111161,0.16166908950994544,0.16270093027928353,0.16367832277775407,0.16460869586133237,0.16549844399627286,0.16635295434558137,0.1671766553408768],[0.10923408734557034,0.10443131277813991,0.0995390825811189,0.09461525833147717,0.08973510409773867,0.08499410980991547,0.08051009690877696,0.07642334486737247,0.07289273940932471,0.07008548755724452,0.06815874565549705,0.06723467532377313,0.06737556536850886,0.06856911551251803,0.07073112917785124,0.07372422244486775,0.07738369013407342,0.08154096172167842,0.08603956712870811,0.0907433063160354,0.09553872034286835,0.1003342623468986,0.10505795001936437,0.10965456087256838,0.11408290452005057,0.11831339256237329,0.12232596400282905,0.1261083500072591,0.12965463400587107,0.13296405730957567,0.13604002391447634,0.1388892648878919,0.14152112995505217,0.14394698057044258,0.1461796645378032,0.14823305711622872,0.1501216575937715,0.15186023361487216,0.15346350818835433,0.15494588633352216,0.1563212197852429,0.15760260911413046,0.15880224307086174,0.15993127499296023,0.1609997357924769,0.16201648246281725,0.1629891803012872,0.1639243162421544,0.16482723992875772,0.16570222850414504],[0.10567116109375395,0.10053932506709129,0.09527670347697945,0.08993829921602575,0.08459858870079213,0.07935609468670413,0.07433807103956655,0.0697039574998157,0.06564478421730631,0.06237387750552761,0.06010368706087051,0.05900775010473112,0.05917768960535017,0.0605958483548987,0.06314035249489497,0.06661930780626403,0.07081414542726806,0.07551375392929419,0.08053319053139522,0.08571988937006368,0.09095271165841791,0.09613797972557636,0.10120481726222716,0.10610082531822132,0.11078842749562448,0.11524190647452127,0.11944504109552173,0.12338922858023078,0.12707198549750293,0.13049573971297446,0.1336668443966702,0.1365947612289049,0.1392913728014189,0.14177039427644172,0.14404686223252736,0.14613668481483413,0.1480562422097542,0.1498220303442738,0.15145034373588803,0.15295699568957974,0.1543570756172174,0.15566474419136592,0.15689306739453873,0.15805389035768175,0.15915775129145723,0.16021383491475125,0.16122996370506018,0.1622126241671599,0.16316702426365515,0.16409717727785478],[0.10228852446470428,0.09685036312610942,0.09123626653775331,0.08549537679031749,0.07969734991494777,0.0739387127799144,0.0683507154293706,0.06310786229099422,0.05843411661768643,0.05459954436004155,0.051895245538901284,0.0505764658860288,0.05078490428848045,0.05249370322281763,0.055517845092164536,0.059581271833654,0.06439173658929503,0.06968823296481849,0.0752583706009422,0.08093790315256436,0.086603368846711,0.09216364787743432,0.0975526143499005,0.10272334482870268,0.10764372646835384,0.11229316221997199,0.11666009026158292,0.12074009499430077,0.1245344453561956,0.12804894223159297,0.13129299037643047,0.134278834237927,0.13702091409704706,0.1395353112815991,0.14183926031818453,0.14395071282617752,0.14588794334406932,0.14766919149734228,0.14931233817829653,0.15083461582041827,0.1522523544688693,0.15358076621485486,0.15483377072622506,0.15602386414833688,0.15716203268086892,0.1582577108028089,0.15931878258592194,0.16035162297960265,0.16136117452856552,0.16235105383264437],[0.0991305300117428,0.09342186824049609,0.08749088878318949,0.08137789585132678,0.07514318519629416,0.06887469391652781,0.06269886944897936,0.056795443441503224,0.05141484829773112,0.046890423944294456,0.04362314022025228,0.042003433853538254,0.04226526137280815,0.04436442664483111,0.048002463760465255,0.0527700077382919,0.058277777095326125,0.0642133010241668,0.07034486471886668,0.07650628438793476,0.08257990211075053,0.08848303381350421,0.0941582503113702,0.09956662900338449,0.10468307208380623,0.10949301202540715,0.1139900429204215,0.11817417434806878,0.12205050909744751,0.1256282132262986,0.12891968987336958,0.1319398960768374,0.13470576039176083,0.1372356719284258,0.1395490207164828,0.14166577631802088,0.14360609709727518,0.1453899668959288,0.14703685924473875,0.1485654317314861,0.14999325475585423,0.15133657964095085,0.15261015097253233,0.15382706718141628,0.15499869190775623,0.15613461677327398,0.1572426740583734,0.15832899566443878,0.15939811285009328,0.16045308973547634],[0.09623440418266536,0.09030484533861621,0.08410902007798368,0.07767612431712846,0.07105300692136196,0.06431198724151821,0.057563274594569634,0.050974971492822194,0.04480421146923519,0.039438365474710475,0.03542041847117743,0.03337126608853493,0.03371203142843914,0.036361608090116876,0.04080007415206768,0.04640619868948097,0.05267725030872941,0.05926402011326241,0.06593512162372983,0.07253770560498213,0.07896986419149729,0.08516329679388894,0.0910726291606641,0.09666872245151598,0.10193434850647881,0.10686128946640769,0.11144831689202275,0.11569972942113137,0.11962425437611278,0.1232341912408084,0.12654471766223793,0.1295733047832028,0.13233920552862297,0.13486299096991328,0.1371661183073922,0.13927052055763076,0.14119821334032195,0.14297091851037297,0.14460970785603935,0.1461346726562261,0.14756462649402055,0.14891684930735105,0.15020688022280176,0.15144836534452766,0.15265296452264152,0.15383031844687609,0.15498807449561544,0.15613196692631554,0.15726594450462691,0.15839233675928183],[0.09362608152160963,0.08753835761711241,0.08114727638323807,0.07447014458814855,0.06753810979368688,0.06040267504671644,0.05314691633709057,0.04590612703146663,0.038907646791658125,0.032547003288767765,0.027507632881652408,0.024798027060395765,0.025267016745279484,0.02874108430219726,0.034226922572420465,0.04078960377179519,0.047838058906065344,0.05503218671708184,0.062172804893703186,0.06913801267903472,0.07585042819603027,0.08226014448529977,0.0883354170182405,0.09405725838679907,0.09941610132574458,0.10440961463589055,0.10904119494534094,0.11331887266219172,0.11725448053397365,0.12086299187929879,0.12416196836608581,0.12717107672456698,0.12991164635105568,0.1324062486637677,0.1346782860174154,0.1367515838177568,0.1386499845662012,0.1403969469893784,0.14201515708578064,0.14352616068563456,0.14495002879057142,0.14630506739918098,0.1476075826869524,0.14887171037111527,0.1501093150617788,0.15132996170654875,0.15254095727957992,0.15374745707193385,0.15495262669264237,0.15615784848136346],[0.0913161991197427,0.08514385336549392,0.07864240840967684,0.07181856170286588,0.06468863602735964,0.057282754002484164,0.049652200441523464,0.04188411104770627,0.03413473929655704,0.026714386354365856,0.020317864445259303,0.016494344925980932,0.01720328460198652,0.021986295218835678,0.02877108608123893,0.03630164932908094,0.04403060381434166,0.05170296368133084,0.059183213134759875,0.06639145619896962,0.07327770174923169,0.07981022220902122,0.0859696469692883,0.09174563668022209,0.09713483157174736,0.10213948405377488,0.10676648680305108,0.11102664267128275,0.11493408720293503,0.11850580723836182,0.12176121695443833,0.12472176355816413,0.12741054243553146,0.1298519076947415,0.13207106959779158,0.13409367569614958,0.13594537761530928,0.13765139021414877,0.1392360540001027,0.14072241487314568,0.14213183717084577,0.14348366634038148,0.1447949562591735,0.14608027333769952,0.1473515853409179,0.14861823780967373,0.14988701561651646,0.15116228214546648,0.15244618437129093,0.1537389091164431],[0.08929692626649592,0.08312031592692752,0.07660382687785212,0.06974687904455351,0.06255538131108765,0.05504378792376751,0.047238327163321055,0.03918312341097095,0.030954702278430522,0.022706278357252557,0.014851753038981322,0.009096226910201562,0.010334212888808056,0.017077691459489844,0.02511064010246093,0.03334859860707491,0.04149232563115441,0.049415240663252896,0.057047234156333726,0.06434392574566351,0.07127591237177504,0.07782407023556316,0.08397708638972501,0.08972995612816784,0.09508296373617109,0.1000409375456825,0.10461267599918016,0.10881048557128546,0.1126497911242099,0.11614878894808145,0.11932811835737923,0.12221053193680856,0.12482054857046912,0.12718407778761304,0.12932800889905888,0.13127976383642284,0.13306681832536243,0.13471620166371576,0.1362539904632703,0.13770481571624463,0.139091404945149,0.14043418157677215,0.14175094184095305,0.1430566255028736,0.1443631909673198,0.14567959838571432,0.14701189716433444,0.14836340756249236,0.14973498062028248,0.1511253169774627],[0.08754030600638467,0.08144134580863535,0.07500852703533707,0.06823861537506906,0.06113396884225524,0.053703999366739454,0.04596713715397284,0.03795403621838781,0.029714492148483276,0.02133846852786572,0.013054716811308592,0.006132008844340687,0.00784522185305813,0.015531300980455237,0.023874980299027425,0.03220008482278216,0.040339802162749336,0.0482149923053618,0.05577608376764512,0.06298883967102012,0.06982929385951626,0.0762813557222667,0.08233540537299633,0.08798734337364783,0.09323789269625168,0.09809206225340746,0.10255872198627398,0.10665025501968127,0.11038225861533861,0.11377326863078746,0.11684448442802096,0.11961947376865369,0.12212384067318992,0.12438484370650525,0.12643095769407778,0.12829137833110119,0.12999547621093469,0.13157221398489904,0.13304954702149005,0.13445383329709087,0.13580928155016037,0.13713746732725257,0.13845694408947096,0.1397829710906855,0.14112737180487156,0.14249852720152226,0.14390149833685453,0.14533826377609377,0.1468080503310254,0.14830773116277854],[0.08599858271541161,0.08005503913902762,0.07380003605421383,0.06723231732941594,0.060357731802376705,0.053191912764648734,0.04576468048045346,0.03812865707672313,0.030379718957893966,0.022716890491765465,0.015662086121151265,0.01093196339562722,0.011961498415007026,0.017750744850972385,0.02508787647057523,0.03279576122825889,0.04049535842819425,0.04802504258836303,0.05529810643387187,0.06226123178213846,0.06887949537542674,0.07512987322910292,0.08099796751969571,0.08647614577575098,0.09156238374309311,0.09625949913270593,0.1005746197062877,0.10451879556096501,0.10810669568233441,0.11135634385519227,0.11428885771817669,0.11692816110942165,0.11930064577518311,0.12143476494268325,0.12336054862934913,0.1251090389708862,0.1267116530932889,0.12819949061062924,0.129602611881186,0.13094932064585227,0.13226548946807676,0.13357396749848766,0.1348941069032827,0.13624143684448986,0.13762750292174952,0.1390598768648258,0.14054232778838577,0.1420751343089098,0.14365550776911445,0.1452780916044279],[0.08460661461447394,0.0788869276058011,0.07289203572352068,0.06662605047079331,0.06010323607143659,0.05335280713066109,0.04642722818012139,0.039418325009281954,0.032492166624926766,0.025971213774425746,0.020525008042214684,0.017440117511076363,0.018087258927220375,0.02212427203981554,0.028029785307123654,0.03472978112400339,0.04169255608575168,0.048653013478396914,0.05546569960050251,0.062043253182265126,0.06832987738610131,0.07428891841280463,0.07989651882880298,0.08513811519997037,0.09000638318058322,0.09449997630514265,0.09862272523243516,0.10238311069025177,0.10579389421360517,0.1088718272953955,0.11163738015871033,0.11411444464609478,0.11632997599584625,0.1183135478034565,0.12009680447706822,0.12171280657619438,0.12319527663025588,0.12457776589463429,0.12589277501046772,0.12717087222976087,0.12843986005051652,0.12972404319697478,0.1310436468515975,0.13241442381791482,0.13384747393066898,0.135349280636988,0.13692195098310883,0.1385636290071265,0.1402690409159667,0.1420301245542742],[0.08328604403604985,0.07784550629002758,0.07217596471501556,0.06628834148307451,0.060206963416184124,0.053976115788569326,0.04767090372764377,0.04141645186743436,0.0354230590923767,0.030048074211172348,0.025878166889638808,0.023715470198808083,0.024180668887276154,0.027127971849029774,0.03180108871771926,0.037448152558288345,0.04356188367988223,0.049834881595663114,0.05608015028579563,0.06217959319185307,0.0680557275936872,0.07365641052479278,0.07894636611676664,0.083902310644678,0.08851005495900863,0.09276274190088898,0.09665975821239374,0.10020605231788453,0.10341168909525546,0.10629152698493724,0.10886493417180708,0.11115548054077022,0.11319055670135637,0.11500088402772368,0.11661989242512244,0.11808295660398288,0.11942649746414878,0.12068697240698112,0.12189979576732045,0.123098246030081,0.1243124274699867,0.12556835775411956,0.12688724807143092,0.1282850281777126,0.12977214691891792,0.1313536525972882,0.13302953126421208,0.1347952589007806,0.13664250863013072,0.13855994799842397],[0.08195057550609366,0.07682930972986732,0.07153085130024672,0.06607244031279794,0.060487100456328116,0.05483087276843668,0.049193836600184906,0.043717188654179055,0.03861865930933375,0.03422368635619765,0.03097860602442911,0.02937742398451119,0.029741083866820298,0.03199616342682833,0.03573011523050963,0.040445296484846675,0.045729475176001184,0.05128877217912529,0.05692334354990724,0.06249746195672397,0.06791756833134995,0.07311816843226152,0.07805309692563248,0.08269013212121461,0.08700766645475275,0.09099264769337365,0.09463931312805844,0.09794841608283812,0.10092674581564152,0.1035868015084632,0.10594651735926135,0.10802895941118162,0.10986193191622734,0.11147744567531949,0.11291101562678904,0.114200771820545,0.11538638779862043,0.11650785318373641,0.11760414146286538,0.11871184660228921,0.1198638791961448,0.12108832004432292,0.1224075231389974,0.12383754014183657,0.1253879068456526,0.12706179407959933,0.12885648795837376,0.13076413397237863,0.1327726607939837,0.13486679440023383],[0.08051159520716784,0.07573431676566501,0.07083334568805867,0.06583033299731303,0.06076375294368101,0.05569576833469506,0.05072161144055918,0.04598197808438229,0.041677273444628175,0.03807702481746722,0.03550596763081214,0.03427837361562193,0.034578873510565,0.036366437252154,0.039396848748604635,0.043338522425967425,0.047876219728458305,0.05275539453321116,0.057784990536640435,0.062825266995637,0.06777432411651674,0.07255746313095332,0.0771197013517622,0.0814207683280873,0.08543185790223544,0.0891335738499659,0.09251466904987789,0.0955712973624425,0.09830657739946165,0.10073031960251713,0.10285880225866872,0.10471450519519694,0.10632572684431031,0.10772602495009548,0.10895343657433858,0.11004945188519116,0.1110577403016942,0.1120226573300645,0.11298759419396938,0.11399326596277316,0.11507606093868732,0.11626658729434022,0.11758854642736002,0.11905803415329419,0.12068332412547185,0.12246513141411987,0.12439729951356915,0.12646781195066972,0.12866000694154536,0.13095387149962773],[0.07888345854795391,0.07446066832667862,0.06996637978332441,0.06542401818669104,0.06087362067583668,0.05637771976314976,0.05202839560509404,0.04795491866639204,0.044329643366620194,0.04136618576196078,0.03929935621170892,0.03833748052721813,0.038596057366876164,0.040050921758029864,0.04254818664292243,0.045861768191368675,0.04975509680384205,0.05401822639416734,0.05848001116895563,0.06300642043862938,0.06749405447952835,0.07186336324104241,0.07605312306251791,0.0800164095606213,0.08371785591509813,0.08713189234992723,0.09024168702783918,0.0930385595266498,0.0955216857776683,0.09769795060494235,0.09958183092864888,0.10119521153227565,0.10256704894225481,0.10373281072422504,0.10473363101379135,0.10561514215228938,0.10642597015864522,0.10721592006962109,0.10803392448451027,0.1089258792453493,0.10993253399329424,0.11108762979743152,0.1124164700778931,0.11393506997490221,0.11564995837648094,0.11755862084891634,0.11965049054410413,0.1219083356051997,0.12430986554260791,0.12682938533167934],[0.07698799675036101,0.07291809656276894,0.06882567705237957,0.06473314747459274,0.060678459389730086,0.05671986263397225,0.052940767234947096,0.049453725910734776,0.046401297160342934,0.04394973307835073,0.042270392661689256,0.041506956940942356,0.04173672565532607,0.04294540958879924,0.04503166660784683,0.047837683106019144,0.05118632726949354,0.05490849924684682,0.058856555497672575,0.06290755412991489,0.06696136548171992,0.0709371079069894,0.07476964290870593,0.07840677921100184,0.08180730214323258,0.08493972818637983,0.08778161894808416,0.09031928578413226,0.09254773435349177,0.0944707196947989,0.0961007999832058,0.0974592891341099,0.09857601577563116,0.09948880160961517,0.10024258018332735,0.10088809315691709,0.10148013111034017,0.10207533407477333,0.10272963329176903,0.10349549299057008,0.104419183458808,0.10553836236115503,0.106880238967876,0.10846053528577865,0.11028334710472626,0.11234187316646957,0.11461985750044754,0.11709350866780407,0.1197336340437416,0.1225077523839153],[0.07475804577629987,0.07102988533475492,0.067324049217767,0.06365933881447676,0.060068634681615815,0.056602698363307245,0.053333356814275375,0.05035507060621055,0.047783184557724616,0.045746478518802654,0.04437191402487418,0.043762177004162704,0.0439719707890947,0.04499332914035123,0.046757653269677034,0.049152815190034845,0.052045907806778334,0.05530238899360759,0.05879770979413047,0.062422197506227364,0.06608171882722554,0.06969640734494728,0.07319889765409356,0.07653277784583412,0.07965151454652278,0.08251786741547346,0.0851037073957112,0.08739012082366304,0.08936768083393958,0.09103677703696977,0.09240790345339271,0.09350180860486465,0.09434940988057876,0.09499136927459381,0.09547722466327459,0.09586397811901679,0.09621407049848381,0.09659272937764964,0.09706476970521752,0.09769104595056999,0.09852487700472487,0.09960885168345854,0.10097243186241865,0.10263067864643648,0.10458424707869503,0.1068205762677848,0.10931601067390458,0.1120384771105383,0.11495032818354041,0.11801102816527442],[0.072140005645459,0.06873548403322816,0.06539384631946348,0.062128025158552175,0.05896358169065767,0.05594188244515948,0.053122174493188304,0.05058170421151529,0.04841274863834771,0.04671535285936006,0.04558521114378961,0.04509800681594974,0.04529425449471664,0.04617027496222527,0.04767910553269533,0.04974042159813043,0.052254584819600935,0.055115566156429735,0.05821990470808317,0.06147149664924402,0.0647833932349245,0.06807799016265267,0.07128663528962288,0.07434923909186517,0.07721413705508692,0.07983825324898484,0.08218751692411075,0.0842374484670178,0.08597382596490617,0.08739334853879947,0.08850421572914745,0.08932653774581174,0.08989247772862873,0.09024600636448865,0.09044212747211372,0.09054542183965744,0.09062777249216503,0.09076519752763426,0.09103384203472606,0.09150536598491374,0.09224217606110774,0.09329311667075858,0.09469027501168191,0.09644741312732143,0.09856023574626697,0.10100833416994369,0.10375834321558836,0.10676770306642552,0.10998844574373376,0.1133705739219292],[0.06909556460579706,0.06599204928061947,0.06298807766212844,0.06008875379121742,0.05731068192983235,0.054684896436279946,0.05225829983301999,0.0500929247788218,0.048262370854390384,0.04684501090149357,0.0459142402554408,0.04552724070144309,0.04571501673722886,0.04647681922441551,0.04778070910932401,0.04956948912354267,0.05176926228206468,0.054297669961252966,0.0570700682807127,0.06000334286492886,0.06301793643886497,0.06603888203524716,0.06899647268772323,0.07182693302866554,0.07447323771397815,0.0768860871364427,0.079024990007322,0.0808593873224856,0.08236975773105518,0.08354865274439079,0.08440161097122759,0.08494788803680009,0.08522091083083022,0.08526832221872442,0.085151431117557,0.08494383670505944,0.0847289799701645,0.08459642824915677,0.08463685878728956,0.0849359932556888,0.08556810518190411,0.08659005315144835,0.08803690932291633,0.08992002654935945,0.09222784673156545,0.09492910370882633,0.09797758376722279,0.10131744103442136,0.10488820925696236,0.10862896516186422],[0.06560277601964523,0.06277522424809756,0.06008069439823955,0.05751466898252436,0.055083555650566635,0.05280775249647353,0.050722783781382695,0.048877966346434806,0.047332362360985085,0.04614822574350506,0.04538278637443263,0.0450799171254159,0.045263628617599444,0.04593499128764235,0.04707292440213918,0.04863790139598823,0.050576841842182016,0.05282764719268242,0.05532262823484081,0.05799084813179115,0.06075980445475287,0.06355689901753911,0.06631097645155237,0.06895402164102757,0.07142297852629433,0.07366160184810092,0.07562225678217355,0.0772676097780636,0.0785721845881845,0.07952377697595038,0.0801247231749177,0.08039299737321318,0.08036306982203952,0.0800863878715625,0.07963124912499761,0.07908173106485064,0.07853525789984978,0.0780983867229727,0.0778805715869969,0.07798609241553871,0.07850499257450168,0.07950454250125996,0.0810230588331862,0.08306753619026021,0.08561552779426057,0.08862050780453293,0.09201914912339405,0.09573884227828874,0.09970422219177787,0.10384210312960278],[0.06165667858672048,0.059079433247529546,0.056666422929022756,0.0544016815187953,0.05228033682762809,0.05031220310425508,0.048522822567368847,0.04695152620618568,0.04564665450057073,0.044658732945059954,0.04403300945229646,0.04380307429004022,0.04398700395986393,0.04458654474357253,0.04558868343002507,0.0469682098257991,0.04868995708815106,0.05071012073196005,0.0529768493316169,0.05543072188902334,0.05800569093613696,0.06063076545390569,0.06323237939456006,0.06573719035831668,0.06807500592525854,0.07018159456251205,0.07200123970019204,0.07348899233902666,0.0746126464606031,0.07535449690955896,0.07571294318031176,0.07570397661729537,0.07536253085114603,0.07474357879584662,0.07392271523176872,0.07299577100178092,0.07207679194871854,0.07129357476505338,0.07078006334383821,0.07066550179888291,0.07106140951646246,0.07204886172960356,0.0736693819102428,0.07592211905313727,0.07876790812498392,0.08213845109095057,0.08594757920878272,0.0901018019619286,0.0945085093952041,0.099081403669732],[0.05726962714284682,0.05491791253205805,0.05276042999467572,0.05076764426223101,0.04892222188703546,0.0472235931525281,0.04568900990654701,0.04435075514114915,0.04325008097402657,0.04242937401462155,0.041924690126117985,0.04176075880497719,0.04194958466215764,0.04249217561758677,0.043381566594725654,0.044605005562254815,0.04614404118524993,0.04797265505365669,0.050054660175807814,0.05234184944251146,0.05477389274609536,0.05728018696094714,0.05978321278746499,0.06220266885820796,0.06445970417040355,0.06648079624623905,0.06820107374865983,0.06956707575901418,0.07053905508294672,0.07109298209281371,0.07122240830578724,0.07094031793072066,0.07028103115382175,0.06930211029337253,0.06808602997815719,0.06674106971049322,0.06540046030354714,0.06421835221228082,0.06336097761043456,0.06299202350589804,0.06325326928745593,0.0642446413471418,0.06601007034785342,0.06853442800754472,0.0717522059900221,0.07556366727783767,0.07985237315672833,0.08449957327020906,0.08939376011790898,0.09443577823530447],[0.05247147162198701,0.050322645092162534,0.04839802058983533,0.0466517422072315,0.045052448462372316,0.043589371084620826,0.04227345456386765,0.0411332324602825,0.04020659961750253,0.03953094073036878,0.03913484396075744,0.03903419377301691,0.03923356325389844,0.03973128284842637,0.040524825007383886,0.04161325423840832,0.042995271145245616,0.04466370879187839,0.046598982207390935,0.048764244048830556,0.05110397083466544,0.053546157730302094,0.05600710099285027,0.05839732146965906,0.060627411441004996,0.06261309760556807,0.06427929354754307,0.06556323219149408,0.06641692360847697,0.06680922956806364,0.06672783568340195,0.06618136568969135,0.0652018260335027,0.06384747122613024,0.062205986159171056,0.06039749318316946,0.058576183156556494,0.056928292142065275,0.05566303735202079,0.05499319352834235,0.055105227347779236,0.0561259271218992,0.058098901724752655,0.0609823701277732,0.06466818520348824,0.06901104674670715,0.07385544322241076,0.07905389474970034,0.08447627840560268,0.09001285691240503],[0.04730970114761596,0.04534433611286894,0.043634538152931224,0.042114277669881024,0.04073584420248876,0.03947829240351811,0.03834863658227471,0.037375636537096746,0.03659807927572874,0.036051396096517384,0.035757531376100854,0.035722054609612586,0.03593926677152683,0.03640204541419964,0.037110872638305266,0.038077170367530146,0.03931903893396777,0.04085108032721992,0.04267255144115681,0.04475852494878109,0.047056956913596036,0.049491769610437705,0.05196993092217682,0.05438991984662022,0.056649596983584044,0.058652523099334455,0.06031258981971344,0.061557272112140855,0.062329965191992645,0.06259186842689045,0.062323829283808044,0.06152851465913427,0.06023324935303538,0.05849383273468064,0.05639954654995295,0.054079235707031346,0.05170744841965143,0.049507662227329885,0.04774638646971962,0.04670913497211131,0.04665274768673922,0.04774472217419599,0.0500204942063623,0.05338649020052861,0.057663929788319385,0.06264260357505938,0.06811988157609998,0.07391971348990756,0.07989758311992015,0.08593852274789242],[0.04184967444334846,0.04005257620648066,0.038545678220312914,0.037237110222799644,0.03605919899626935,0.03498049444155432,0.034007051800130146,0.03317302197948164,0.03252348122575313,0.03209531667336662,0.03190378802409385,0.031940834749440934,0.032185654914728815,0.032621667532381424,0.033250993393080526,0.03409932810032448,0.03520868800774297,0.036620719549434015,0.03835729814158171,0.04040616254789948,0.04271643073071349,0.04520380700680286,0.047761540296934205,0.050272557683877936,0.052619780903246226,0.0546935892944758,0.05639666264201263,0.05764693515730682,0.05837943162276849,0.05854763185897007,0.05812488245875881,0.05710631030942819,0.05551170999821704,0.05338997598802063,0.05082579839314604,0.04794939633002751,0.04494954447848032,0.04208775532053017,0.039704741118162246,0.03819821286473673,0.03794590477652212,0.03918282980856719,0.04191349303671673,0.045938190782256236,0.05096048971313254,0.056683964994790115,0.06285819365784084,0.06928727319519083,0.0758227611664841,0.08235340522978424],[0.03617511510281621,0.03453643274650347,0.03322860766138686,0.032125280213229475,0.03113304653614513,0.030208985287320293,0.029362050110295367,0.02863892267209184,0.028098506562778854,0.027783580317898418,0.027701719009897166,0.02782534077439497,0.028110903777647907,0.028526664967576085,0.029075058860829017,0.02979977918480276,0.030774347010534445,0.032075916961657895,0.03375455547378486,0.035810964368350726,0.03819094879088101,0.04079539870896363,0.043497863349114804,0.04616181250018268,0.04865354339079281,0.05085022777114008,0.052644252735941435,0.053945274791474734,0.05468111712333435,0.05479828823636457,0.054262661746956396,0.053060764692323195,0.051202179127766645,0.04872379656828416,0.045697149083158486,0.04224086929658228,0.03854140219042629,0.03488504322129609,0.03169694658283479,0.029551267502297272,0.02905866726628269,0.03058225171685488,0.03402317136578639,0.03895193433694344,0.04488686229685558,0.05144022904514184,0.058334692492924244,0.06537730719115403,0.07243280972048405,0.07940478392016641],[0.03038923266538085,0.028906000616865553,0.027804791822043463,0.026911049905776776,0.02609626978379132,0.0253039683441805,0.024551102459064673,0.0239071734580151,0.023456266544932016,0.02325367643995715,0.023297055521406096,0.02352948686525776,0.023873056906764504,0.024273037956665616,0.024731071405260756,0.02531503741644103,0.02614186050042037,0.027337188450937334,0.02898683012380932,0.031102728259197455,0.03361848618261682,0.03640976307963414,0.039322883142767155,0.04219849017399444,0.044886187998444356,0.04725175637097437,0.04917984945437532,0.050574455522527643,0.05135849571951651,0.05147330957439802,0.05087844429632196,0.049552053953699694,0.04749227844910965,0.04472024519245324,0.041285986890290345,0.03728004274879158,0.03285685371737397,0.02828319540519404,0.024034858524805098,0.020938936285905537,0.020120738027777627,0.022241156096252455,0.026828318392223518,0.03295249431313213,0.03991428443672651,0.047296377283363306,0.05485128385953584,0.06242329073399572,0.06990816783862767,0.07723290207551206],[0.024617353046251254,0.02329628898619588,0.022426839058619287,0.02176342646158838,0.021127023276525842,0.02044365056567125,0.019744911712637342,0.019138162707793616,0.01875084726165925,0.018661968938846366,0.018855149456690447,0.019227862504080477,0.019650686419677234,0.020036047602706702,0.020384369243367353,0.02079701368100641,0.021452246049282683,0.022543931805888724,0.024202892328075605,0.026444729969858572,0.0291734346368626,0.03222407689317447,0.03540827874981362,0.038543350592571614,0.04146549037015081,0.04403362888410718,0.04612915594201979,0.04765431020109475,0.04853043750019459,0.04869656619122861,0.04810844856680625,0.04673813827117211,0.04457421595518767,0.041622941902515136,0.03791103061920256,0.033491835293136,0.02845994186862105,0.022989948787508686,0.017456227806711876,0.01283785350263444,0.011491567587350779,0.014987896916772651,0.02131748450959663,0.028758261346049325,0.03663830788538497,0.04467104303896436,0.05270288380404702,0.06063630092404813,0.06840294186111132,0.07595254096009849],[0.019013534730660055,0.01787743804550536,0.017295709892485165,0.016910954662934668,0.01646853109875712,0.015870839414147853,0.015171919363888065,0.01453785369966042,0.014169875151204124,0.014192248548832142,0.014567319347146734,0.015119192036639743,0.015643182006863536,0.016008856319972023,0.016216395786993427,0.016412673862115264,0.01686335293440902,0.017860956829902467,0.019590162086412906,0.022047360725059133,0.025074988949726516,0.02844945104353203,0.03194573910290413,0.03536424379223037,0.03853606454935586,0.04132065199143709,0.043601945597733074,0.04528496026682824,0.046293204940362875,0.046566863598525805,0.04606159008332764,0.044747795050467595,0.04261035789711556,0.03964877262486583,0.03587787587847462,0.03132965528677124,0.026057756185776892,0.020150837396807883,0.013785998794746275,0.00757842643296195,0.005625543945301994,0.011446566276263654,0.01916853983061234,0.027320664964852668,0.03560716239236345,0.0438958654034463,0.052100688845506636,0.060157173134795516,0.06801480526512028,0.07563370316744847],[0.013779126829844645,0.012884181479303633,0.012705973513852838,0.012695310110800408,0.012486701178817049,0.011955314984187192,0.011183482031326544,0.010416377343771089,0.009977821232216572,0.010085600313281385,0.0106700684022501,0.0114336203146519,0.01206860416614789,0.012397680283965047,0.012422989512257107,0.012347286919177641,0.01255932012759788,0.013498710073103484,0.015402236724592854,0.018187647185711406,0.021588615763417297,0.02531627356280954,0.02912321191475178,0.032809346943372356,0.036213078245000155,0.03920256665604783,0.04166961551464691,0.04352572917621929,0.04469965229370593,0.045135897381363387,0.04479397468884542,0.04364819581280511,0.04168806615239323,0.038919481474898224,0.03536735572798179,0.031081380848894873,0.02614992423413445,0.02073907398170992,0.015225774746477903,0.01072329602582825,0.010134931751340828,0.014599777402921347,0.021405796328812357,0.029044174185165403,0.03700401660285613,0.0450631137876433,0.05309508051892152,0.06101517536460287,0.06876161190965153,0.07628771973501962],[0.009222295122747097,0.008707973278710385,0.009154109919771525,0.009662098195785404,0.009748515174525392,0.009287404916655256,0.008387063380258034,0.00735347174986912,0.006666794704106687,0.0067440425073242724,0.007497933782024114,0.008442411028141318,0.009150112645214696,0.009405854733460131,0.009211195950360872,0.008820071241223085,0.008786505796767066,0.009770709097200073,0.012007383193698531,0.01521487370866089,0.018994141196674086,0.02302673179051634,0.02707746960491869,0.030966238512883448,0.0345489870118027,0.0377074303021644,0.040343591617399095,0.04237689682315642,0.043742700988756274,0.04439173121258056,0.04429025369682389,0.043420996822605605,0.041785107514631006,0.039405825984477116,0.036335406397949147,0.03266873552463957,0.028571681102215075,0.024342522867218823,0.02053886996829033,0.018146712998175135,0.018364136477520835,0.021525436376920573,0.02682381397601863,0.03334225456817187,0.04050147665720907,0.04797109144229883,0.05555270292359359,0.06311746018524773,0.07057616387190817,0.07786448862836692],[0.00595129958946505,0.006120254139784445,0.007398393037646302,0.008450991218528433,0.008832249604579026,0.008486255730865836,0.007542949619270138,0.006292531284638932,0.005230809251959542,0.004960257255905101,0.0055564614002477615,0.006434215063615971,0.007063353149626608,0.007187648104231899,0.006785716823218553,0.006130709938696258,0.005967707219463477,0.00721232235135232,0.009896019028675589,0.013463663961079017,0.017479916054681244,0.021667960041623448,0.02583242004240661,0.029820650419923468,0.03350670752977082,0.03678447279881572,0.039564585195032656,0.04177316682289346,0.04335155806780012,0.044256781678194496,0.04446271703129469,0.04396217494967617,0.042770323281450376,0.040930326118196005,0.03852276189086652,0.035681505959688053,0.032619994115435,0.029670366224713682,0.027322606952009085,0.026199530188155545,0.026855039229519345,0.02945951293538809,0.03373706853604256,0.03922232295521269,0.045490953385392434,0.05222679232720942,0.059207487890818214,0.06627662035342391,0.07332211276488948,0.0802621570945009],[0.0049683821917500355,0.005904597428727097,0.007661098449876097,0.008969411095268123,0.00952314589755021,0.009317846863288506,0.008488202109114922,0.007281469072807513,0.006066548169171802,0.005292074239060555,0.005200118069955586,0.005530459077172545,0.005818230727749677,0.0057585359002270756,0.0052884557531144944,0.004689305403031133,0.004807957323233258,0.006459857490293708,0.009372685304978055,0.012996638888057965,0.016989712772663736,0.02113285217972592,0.02526182045402457,0.029241570193742513,0.03295671431374544,0.03630785663462999,0.03921033358006166,0.04159413302058969,0.043404533429525764,0.04460333543098444,0.045170747553011696,0.045108147673582025,0.04444211829772755,0.0432303609008147,0.04157027491748086,0.039610863737687414,0.03756733137068971,0.03573323504646404,0.0344749524054193,0.034182230676010596,0.035162870915405486,0.0375323685243415,0.04119044004057071,0.045899490929558265,0.051385859282007264,0.057401678077684516,0.06374508081371821,0.0702589234816519,0.07682286591721262,0.0833451861249041],[0.00583620283984981,0.007061262388318619,0.00885254012064892,0.010203982846410905,0.01084652927280832,0.010770104286920525,0.010087431492249178,0.00899457429562822,0.007749626379184292,0.006632955707062716,0.0058541922171055595,0.005432791282388517,0.005198234529665053,0.00495621272470445,0.004671294123519993,0.004620758351633285,0.005377351968991274,0.007251995764693218,0.010039966373636928,0.013431350471891574,0.01718873973097578,0.02113224398364989,0.025114595512415055,0.029008987111952884,0.032704105841789406,0.036102484852700664,0.03912043096847421,0.0416887748729375,0.04375413591785787,0.04528062174055728,0.046252021772273146,0.046674649674539014,0.04658104882438914,0.04603476053380205,0.04513615299070166,0.04402866792351219,0.042903343166212894,0.04199679744291911,0.04157496116076129,0.04189589816623752,0.04315631241445651,0.04544483261924706,0.04872993277171631,0.0528875845921897,0.057746837502659895,0.06312881395780622,0.06886947139080574,0.07482862899215592,0.08089107329168083,0.08696421505921079],[0.006795962623469816,0.008110446674299396,0.009902302383707684,0.011298698510499245,0.012036113131693399,0.012087627764553912,0.011538119694011306,0.010538007745877475,0.009274091833597571,0.007939551490108719,0.0067022680033589485,0.005684246593232968,0.004967262551338476,0.004618938794268086,0.004711465106543754,0.005337705428754254,0.006602513965854267,0.00854671011962753,0.011112464228384975,0.014182846582352329,0.01762358862850657,0.021301442930301718,0.025089678412794136,0.028869827643180926,0.032532930123560476,0.03598098642001262,0.03912863012017654,0.04190492087627889,0.04425521636539741,0.04614315399478019,0.04755282383248674,0.04849122809183718,0.04899108107854666,0.049113866589740526,0.04895276420700705,0.04863448587990859,0.04831819141443419,0.048188724762871636,0.04844132238156636,0.049257198952541714,0.050774680907583684,0.053066027627568936,0.056129959517494984,0.059902155947122844,0.06427683390835491,0.06912951963240985,0.07433452018827055,0.07977547607704129,0.08535028972683475,0.09097245938212023],[0.007046387512733497,0.008454582470321765,0.010344673816580599,0.011859891022354452,0.012733471189013662,0.01292655240591299,0.012504151736017136,0.011587523911124279,0.010326239822885911,0.008877534607748589,0.00739740152095898,0.006056927375159911,0.005087895779697396,0.004776564736015966,0.005237246720214012,0.006298206331165611,0.007796228890818387,0.009700183850223818,0.012028623338926105,0.01477682461284146,0.01789726902565058,0.021308471358098387,0.024909522239243306,0.028592021405418493,0.03224852972464859,0.0357784778200584,0.039092414858517666,0.04211518849204238,0.044788450354884865,0.04707276554063879,0.04894952007585579,0.05042273402656685,0.051520772784786506,0.05229777674273078,0.05283437276481069,0.05323688714173224,0.053633926004916135,0.054169059213210184,0.05498884650816574,0.056226941688574845,0.05798725562052477,0.06033086116167212,0.06327081621861548,0.0667760918545369,0.07078221677494126,0.07520443553550102,0.07994973047222412,0.08492582124609889,0.09004686524708015,0.09523645518792931],[0.0064654667234720865,0.007993098299561562,0.010081407502685798,0.01178416440937871,0.01282714528405109,0.013169058414081272,0.012868154735559497,0.012035698219181372,0.010812108491786179,0.009353630737347915,0.007834053237306899,0.00647242192497013,0.005574558470011038,0.005453489998787702,0.006122037868699946,0.007294698092984683,0.008756959025854135,0.0104741429067138,0.012506646188437342,0.014919195282129885,0.01773077885453569,0.020904777190104508,0.02436207394328885,0.02799990456777359,0.03170774471681858,0.035378372235007685,0.038914976871294714,0.042235631739894794,0.04527615824199717,0.04799205639150137,0.05035989016006062,0.05237830794675814,0.054068704910955466,0.05547536524174171,0.05666474518713572,0.05772339010315616,0.05875388847843282,0.059868376725825935,0.06117956040268484,0.06279004361741622,0.06478172101420099,0.06720755327617503,0.07008769725986592,0.0734106827137302,0.07713876587827162,0.0812155757644389,0.085574072228169,0.09014341691946874,0.09485412697789213,0.09964147940019406],[0.005403559213129176,0.006961218198697524,0.009268911734647266,0.01116473649150279,0.012361931056158878,0.012824575131870521,0.012615592923915174,0.011852805137184539,0.01069019007778778,0.009310152939188476,0.007928465430607967,0.006810334299589603,0.006249739162110901,0.006408248763583944,0.007150970813160458,0.008207335745411937,0.009416356489941565,0.010781604206324224,0.012413564136756343,0.014443456835607006,0.016950441091320448,0.019932062877487663,0.02331683517005782,0.026993767830984502,0.03083847686332445,0.034729975448912875,0.03855991955842935,0.0422373322258141,0.04569094707302655,0.04887035570992664,0.05174653038927661,0.05431194378013738,0.05658029919751382,0.058585741694783575,0.06038131364591852,0.06203635426615505,0.06363255621135591,0.06525853495593453,0.06700307321827653,0.06894764161904075,0.07115922850820766,0.07368471507101988,0.07654782684266959,0.07974909435291522,0.08326850816032555,0.08706998332417434,0.09110655245158623,0.09532536163799198,0.09967188227805181,0.10409309800216537],[0.005085102180393543,0.00613443858015694,0.008380285796117354,0.010304086022610038,0.011533395502845701,0.012015465987590271,0.01181431945114385,0.011061615203824978,0.009941527447662312,0.008686989779157175,0.007576993612581409,0.006902438271712271,0.006841693248776269,0.007321197029113011,0.008089816662775653,0.00892289151519548,0.009733581240884968,0.010591440229262339,0.011690059476770168,0.013261667212557969,0.015464142613239274,0.01831898430416052,0.021734658650014435,0.025565345345526805,0.02965549258693895,0.033861680658939484,0.038060796832736526,0.04215232228373749,0.04605851853077612,0.04972395830370309,0.053114849891149944,0.05621822326331607,0.059040896275302755,0.06160806976907367,0.06396136609244585,0.0661561251721867,0.06825782291785223,0.07033759772766097,0.0724670657866829,0.0747128434365119,0.07713140131873865,0.07976495393058569,0.08263897098720013,0.08576159476493274,0.08912486151226609,0.0927072955906998,0.09647727535021199,0.10039657959435114,0.10442366019448705,0.1085163707111256],[0.007048622467348303,0.006913272869716845,0.008308040676035211,0.009788365696110874,0.010748961013970763,0.01103277278738781,0.010668014911621638,0.009789085331582478,0.008619663222578565,0.007475424193785121,0.006734187275668859,0.0066671364034593126,0.007206960714598766,0.008028146305697434,0.008818214156089686,0.009395498044522825,0.009726164469337327,0.009940875788456932,0.01034657584758573,0.011352210366076634,0.01325808178392955,0.016094782946659673,0.01969139920622141,0.023821570871828956,0.02827857965746712,0.032892117146832524,0.03752613404609932,0.042074071048090314,0.04645511307636759,0.05061160480007462,0.05450718470114699,0.058125239253099883,0.061467383825296734,0.06455174899803831,0.06741089780467453,0.07008924413912719,0.07263990587281781,0.07512102066745698,0.07759167678354392,0.08010774523220254,0.08271800529346264,0.08546098853466404,0.08836289818545223,0.09143679756975152,0.09468304862475031,0.09809078474387986,0.10164007620472695,0.10530441326276549,0.10905317836015385,0.11285387099556013],[0.010887690164101455,0.009798281173294078,0.009915812529756974,0.010413604018506602,0.01068219907839578,0.010447201723744946,0.009661517198381743,0.00843504384455111,0.00703042852000561,0.005905275192230284,0.005621996147198873,0.006306849037409241,0.007473570485700504,0.008610794584367623,0.009414592434690946,0.009738213264278733,0.009562785998355455,0.009031462734358758,0.008545023698765938,0.008808123054693971,0.010446044115035816,0.013454928786945103,0.017438153082271427,0.02202492690981432,0.026952948692920694,0.03203623957789157,0.03713695490313335,0.042150619596343135,0.046998813154686625,0.05162530152283812,0.055993678996100145,0.060085608150329,0.06389920248342304,0.06744730037892273,0.07075547875510275,0.07385971853049028,0.07680369399937781,0.07963572788855451,0.0824055334946239,0.08516094355175689,0.0879448825203417,0.09079285339422996,0.09373116877197421,0.09677606243016844,0.09993369381564393,0.10320093622879623,0.1065667501275874,0.11001390254454628,0.11352080149901524,0.11706325694906394],[0.015755685155946945,0.014076597621851435,0.013194633303489241,0.012652495782756555,0.012030709416628201,0.011070808401046801,0.00968947454468702,0.007970270434727363,0.006205623717099531,0.005031588439196392,0.00521706146672146,0.006530378194242352,0.008112797947564513,0.009424503605479723,0.010195733216742338,0.010290454816609116,0.009668598160016839,0.008415567248981027,0.006887585101820812,0.006104589372076159,0.007510956201387788,0.010963585305697316,0.015516956972156007,0.020638916395339206,0.026055573914007344,0.031594141874023145,0.03712966570683898,0.04256694278395786,0.047833519526410864,0.052876450029281166,0.05766038809694516,0.06216610846421319,0.06638907728617033,0.07033789107528422,0.07403249053859047,0.07750210673379264,0.0807829406721144,0.08391562420063163,0.08694255981298728,0.08990528319200529,0.09284202386233685,0.09578564520693247,0.09876211877443351,0.10178963123907811,0.10487834672213914,0.10803076950268205,0.1112425894694708,0.11450385633137862,0.11780032144603528,0.12111480331879729],[0.02125795520710428,0.019189387499807056,0.017646364848904545,0.016336034936181174,0.01498541773872529,0.013414961855503083,0.011575997027979082,0.009579472364416343,0.00775559524394616,0.006711830984923934,0.00697447730833316,0.008236517699494817,0.009749590507184646,0.01098240045464322,0.011638978086997622,0.011560071030356344,0.01068132760552491,0.009043668259446755,0.006902620279782688,0.005225526326744883,0.006216355342513946,0.009922927318678923,0.0148340453724522,0.020299602010085103,0.026044146375223756,0.03190283208065467,0.0377567746509546,0.04351459291585751,0.04910587152295995,0.05447822949365756,0.05959557000733969,0.06443668403252278,0.06899388526791259,0.07327153565914311,0.07728439743349454,0.08105578993529777,0.08461556275966681,0.08799792918096787,0.09123923623975838,0.09437577622913433,0.09744176259759867,0.1004675954542942,0.1034785245311215,0.10649378174467519,0.10952620742470125,0.11258234324067891,0.11566292080333732,0.11876364534337891,0.12187616198970548,0.12498909677039793]],[],[],[[0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669,0.8201380696084669],[0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453,0.8165164948691453],[0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903,0.8125458755238903],[0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027,0.8084256215339027],[0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575,0.8043712487358575],[0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332,0.8005969218469332],[0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797,0.7972988118281797],[0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365,0.7946392999826365],[0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965,0.7927319514272965],[0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111,0.7916273561272111],[0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265,0.7913010598529265],[0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278,0.7916488642179278],[0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763,0.7924962355772763],[0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968,0.7936182938572968],[0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131,0.7947619001596131],[0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483,0.7956658371249483],[0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178,0.796077881068178],[0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903,0.7957685065998903],[0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762,0.7945413768096762],[0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829,0.7922408945144829],[0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244,0.7887569238884244],[0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065,0.7840262485213065],[0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787,0.7780302749634787],[0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805,0.7707898728294805],[0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059,0.7623591303948059],[0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174,0.7528191806759174],[0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274,0.7422725281882274],[0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525,0.7308379891073525],[0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333,0.7186462408659333],[0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904,0.7058359295725904],[0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428,0.6925502641713428],[0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994,0.6789340214753994],[0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181,0.6651308903448181],[0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134,0.6512810934655134],[0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276,0.6375192398936276],[0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122,0.6239723797299122],[0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658,0.6107582528416658],[0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823,0.5979837446731823],[0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981,0.5857435811363981],[0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819,0.5741193077443819],[0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813,0.5631786018052813],[0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274,0.5529749581171274],[0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734,0.5435477683735734],[0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614,0.5349227860061614],[0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698,0.5271129377237698],[0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785,0.5201194174071785],[0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475,0.5139329822752475],[0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128,0.5085353670782128],[0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879,0.5039007380490879],[0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709,0.4999971211126709]],[[0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998,0.008828291651287998],[0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532,0.008152471428054532],[0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567,0.008891554364414567],[0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837,0.00991739837955837],[0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139,0.01057563497733139],[0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143,0.010637082810870143],[0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836,0.010092769287217836],[0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403,0.009067963566964403],[0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605,0.0078070381612518605],[0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143,0.006688173361929143],[0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392,0.006167795275368392],[0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721,0.006468968828957721],[0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223,0.007332875523591223],[0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912,0.008323137387325912],[0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386,0.009122956176438386],[0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076,0.009569915597575076],[0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934,0.009642991127710934],[0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515,0.009488023920955515],[0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161,0.009468238992601161],[0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524,0.010126448077941524],[0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062,0.011891139682116062],[0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928,0.014784557056209928],[0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213,0.018548934178653213],[0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192,0.022892624469709192],[0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326,0.027578850073343326],[0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859,0.03242649366507859],[0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288,0.03729661352339288],[0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424,0.042082516688144424],[0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145,0.046703903322254145],[0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496,0.05110341796866496],[0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553,0.05524440511625553],[0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259,0.0591091768875259],[0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438,0.06269739449189438],[0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475,0.06602431503005475],[0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081,0.0691187361039081],[0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639,0.0720205293456639],[0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909,0.07477771763457909],[0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199,0.07744313252487199],[0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142,0.08007078771453142],[0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658,0.08271220612474658],[0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834,0.08541301507662834],[0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797,0.0882101457682797],[0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226,0.09112992062747226],[0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912,0.09418718997811912],[0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134,0.09738551886918134],[0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934,0.10071827138743934],[0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534,0.10417033365968534],[0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174,0.10772017750593174],[0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419,0.1113419893532419],[0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641,0.11500765208357641]],[],[]]},{"xaxis.title":"gamma","xaxis2.title":"gamma","xaxis.range":[-6.0,6.0],"xaxis2.range":[-6.0,6.0],"xaxis.type":"log","xaxis2.type":"log"}],"label":"gamma","method":"update"}],"direction":"up","x":0.35,"xanchor":"left","y":-0.29,"yanchor":"middle"},{"buttons":[{"args":[{"visible":[false,false,false,false,true,true,true,true]},{"yaxis.title":"gamma","yaxis.range":[-6.0,6.0],"yaxis2.range":[-6.0,6.0],"yaxis.type":"log","yaxis2.type":"log"}],"label":"gamma","method":"update"}],"direction":"up","x":0.35,"xanchor":"left","y":-0.43,"yanchor":"middle"}],"xaxis":{"anchor":"y","autorange":false,"domain":[0.05,0.45],"exponentformat":"e","range":[-9.0,6.0],"tickfont":{"size":11},"tickmode":"auto","title":{"text":"C"},"type":"log"},"yaxis":{"anchor":"x","autorange":false,"domain":[0,1],"exponentformat":"e","range":[-6.0,6.0],"tickfont":{"size":11},"tickmode":"auto","title":{"text":"gamma"},"type":"log"},"xaxis2":{"anchor":"y2","autorange":false,"domain":[0.6,1],"exponentformat":"e","range":[-9.0,6.0],"tickfont":{"size":11},"tickmode":"auto","title":{"text":"C"},"type":"log"},"yaxis2":{"anchor":"x2","autorange":false,"domain":[0,1],"exponentformat":"e","range":[-6.0,6.0],"tickfont":{"size":11},"tickmode":"auto","type":"log"},"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}}},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>

### Comparison

In [62]:
max_accuracy = {"Method": [], "Trial": [], "Accuracy": []}
for k, v in results_svc.items():
    max_accuracy["Method"].extend([k] * (len(v) + 1))
    max_accuracy["Trial"].extend([0] + (v.trial_index + 1).to_list())
    max_accuracy["Accuracy"].extend([0] + v["accuracy"].cummax().tolist())
render_plotly_html(px.line(max_accuracy, x="Trial", y="Accuracy", color="Method"))

<html>
<head><meta charset="utf-8" /></head>
<body>
    <div>                        <script type="text/javascript">window.PlotlyConfig = {MathJaxConfig: 'local'};</script>
        <script charset="utf-8" src="https://cdn.plot.ly/plotly-2.34.0.min.js"></script>                <div id="336aa34a-f367-4800-96e4-e6e7abd2e932" class="plotly-graph-div" style="height:100%; width:100%;"></div>            <script type="text/javascript">                                    window.PLOTLYENV=window.PLOTLYENV || {};                                    if (document.getElementById("336aa34a-f367-4800-96e4-e6e7abd2e932")) {                    Plotly.newPlot(                        "336aa34a-f367-4800-96e4-e6e7abd2e932",                        [{"hovertemplate":"Method=PI\u003cbr\u003eTrial=%{x}\u003cbr\u003eAccuracy=%{y}\u003cextra\u003e\u003c\u002fextra\u003e","legendgroup":"PI","line":{"color":"#636efa","dash":"solid"},"marker":{"symbol":"circle"},"mode":"lines","name":"PI","orientation":"v","showlegend":true,"x":[0,1,2,3,4,5,6,7,8,9,10],"xaxis":"x","y":[0.0,0.452,0.536,0.804,0.816,0.82,0.82,0.82,0.82,0.82,0.82],"yaxis":"y","type":"scatter"},{"hovertemplate":"Method=EI\u003cbr\u003eTrial=%{x}\u003cbr\u003eAccuracy=%{y}\u003cextra\u003e\u003c\u002fextra\u003e","legendgroup":"EI","line":{"color":"#EF553B","dash":"solid"},"marker":{"symbol":"circle"},"mode":"lines","name":"EI","orientation":"v","showlegend":true,"x":[0,1,2,3,4,5,6,7,8,9,10],"xaxis":"x","y":[0.0,0.48,0.496,0.808,0.808,0.808,0.812,0.812,0.812,0.824,0.824],"yaxis":"y","type":"scatter"}],                        {"template":{"data":{"histogram2dcontour":[{"type":"histogram2dcontour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"choropleth":[{"type":"choropleth","colorbar":{"outlinewidth":0,"ticks":""}}],"histogram2d":[{"type":"histogram2d","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmap":[{"type":"heatmap","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"heatmapgl":[{"type":"heatmapgl","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"contourcarpet":[{"type":"contourcarpet","colorbar":{"outlinewidth":0,"ticks":""}}],"contour":[{"type":"contour","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"surface":[{"type":"surface","colorbar":{"outlinewidth":0,"ticks":""},"colorscale":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]]}],"mesh3d":[{"type":"mesh3d","colorbar":{"outlinewidth":0,"ticks":""}}],"scatter":[{"fillpattern":{"fillmode":"overlay","size":10,"solidity":0.2},"type":"scatter"}],"parcoords":[{"type":"parcoords","line":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolargl":[{"type":"scatterpolargl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"bar":[{"error_x":{"color":"#2a3f5f"},"error_y":{"color":"#2a3f5f"},"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"bar"}],"scattergeo":[{"type":"scattergeo","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterpolar":[{"type":"scatterpolar","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"histogram":[{"marker":{"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"histogram"}],"scattergl":[{"type":"scattergl","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatter3d":[{"type":"scatter3d","line":{"colorbar":{"outlinewidth":0,"ticks":""}},"marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattermapbox":[{"type":"scattermapbox","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scatterternary":[{"type":"scatterternary","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"scattercarpet":[{"type":"scattercarpet","marker":{"colorbar":{"outlinewidth":0,"ticks":""}}}],"carpet":[{"aaxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"baxis":{"endlinecolor":"#2a3f5f","gridcolor":"white","linecolor":"white","minorgridcolor":"white","startlinecolor":"#2a3f5f"},"type":"carpet"}],"table":[{"cells":{"fill":{"color":"#EBF0F8"},"line":{"color":"white"}},"header":{"fill":{"color":"#C8D4E3"},"line":{"color":"white"}},"type":"table"}],"barpolar":[{"marker":{"line":{"color":"#E5ECF6","width":0.5},"pattern":{"fillmode":"overlay","size":10,"solidity":0.2}},"type":"barpolar"}],"pie":[{"automargin":true,"type":"pie"}]},"layout":{"autotypenumbers":"strict","colorway":["#636efa","#EF553B","#00cc96","#ab63fa","#FFA15A","#19d3f3","#FF6692","#B6E880","#FF97FF","#FECB52"],"font":{"color":"#2a3f5f"},"hovermode":"closest","hoverlabel":{"align":"left"},"paper_bgcolor":"white","plot_bgcolor":"#E5ECF6","polar":{"bgcolor":"#E5ECF6","angularaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"radialaxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"ternary":{"bgcolor":"#E5ECF6","aaxis":{"gridcolor":"white","linecolor":"white","ticks":""},"baxis":{"gridcolor":"white","linecolor":"white","ticks":""},"caxis":{"gridcolor":"white","linecolor":"white","ticks":""}},"coloraxis":{"colorbar":{"outlinewidth":0,"ticks":""}},"colorscale":{"sequential":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"sequentialminus":[[0.0,"#0d0887"],[0.1111111111111111,"#46039f"],[0.2222222222222222,"#7201a8"],[0.3333333333333333,"#9c179e"],[0.4444444444444444,"#bd3786"],[0.5555555555555556,"#d8576b"],[0.6666666666666666,"#ed7953"],[0.7777777777777778,"#fb9f3a"],[0.8888888888888888,"#fdca26"],[1.0,"#f0f921"]],"diverging":[[0,"#8e0152"],[0.1,"#c51b7d"],[0.2,"#de77ae"],[0.3,"#f1b6da"],[0.4,"#fde0ef"],[0.5,"#f7f7f7"],[0.6,"#e6f5d0"],[0.7,"#b8e186"],[0.8,"#7fbc41"],[0.9,"#4d9221"],[1,"#276419"]]},"xaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"yaxis":{"gridcolor":"white","linecolor":"white","ticks":"","title":{"standoff":15},"zerolinecolor":"white","automargin":true,"zerolinewidth":2},"scene":{"xaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"yaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2},"zaxis":{"backgroundcolor":"#E5ECF6","gridcolor":"white","linecolor":"white","showbackground":true,"ticks":"","zerolinecolor":"white","gridwidth":2}},"shapedefaults":{"line":{"color":"#2a3f5f"}},"annotationdefaults":{"arrowcolor":"#2a3f5f","arrowhead":0,"arrowwidth":1},"geo":{"bgcolor":"white","landcolor":"#E5ECF6","subunitcolor":"white","showland":true,"showlakes":true,"lakecolor":"white"},"title":{"x":0.05},"mapbox":{"style":"light"}}},"xaxis":{"anchor":"y","domain":[0.0,1.0],"title":{"text":"Trial"}},"yaxis":{"anchor":"x","domain":[0.0,1.0],"title":{"text":"Accuracy"}},"legend":{"title":{"text":"Method"},"tracegroupgap":0},"margin":{"t":60}},                        {"responsive": true}                    )                };                            </script>        </div>
</body>
</html>